In [1]:
###IMPORT MODULES AS APPROPRIATE###

In [2]:
import nltk; nltk.download('stopwords')

C:\Users\brady\Anaconda3\lib\site-packages\sklearn\feature_extraction\image.py:167: DeprecationWarning: `np.int` is a deprecated alias for the builtin `int`. To silence this warning, use `int` by itself. Doing this will not modify any behavior and is safe. When replacing `np.int`, you may wish to use e.g. `np.int64` or `np.int32` to specify the precision. If you wish to review your current use, check the release note link for additional information.
Deprecated in NumPy 1.20; for more details and guidance: https://numpy.org/devdocs/release/1.20.0-notes.html#deprecations
  dtype=np.int):
C:\Users\brady\Anaconda3\lib\site-packages\sklearn\linear_model\least_angle.py:35: DeprecationWarning: `np.float` is a deprecated alias for the builtin `float`. To silence this warning, use `float` by itself. Doing this will not modify any behavior and is safe. If you specifically wanted the numpy scalar type, use `np.float64` here.
Deprecated in NumPy 1.20; for more details and guidance: https://numpy.o

True

In [3]:
import re
import numpy as np
import pandas as pd
from pprint import pprint

# Gensim
import gensim
import gensim.corpora as corpora
from gensim.utils import simple_preprocess
from gensim.models import CoherenceModel

# spacy for lemmatization
import spacy

# Plotting tools
import pyLDAvis
import pyLDAvis.gensim  # don't skip this
import matplotlib.pyplot as plt
%matplotlib inline

# Enable logging for gensim - optional
import logging
logging.basicConfig(format='%(asctime)s : %(levelname)s : %(message)s', level=logging.ERROR)

import warnings
warnings.filterwarnings("ignore",category=DeprecationWarning)

C:\Users\brady\Anaconda3\lib\site-packages\pandas\compat\_optional.py:138: UserWarning: Pandas requires version '2.7.0' or newer of 'numexpr' (version '2.6.9' currently installed).
  warnings.warn(msg, UserWarning)
C:\Users\brady\Anaconda3\lib\site-packages\gensim\similarities\__init__.py:15: UserWarning: The gensim.similarities.levenshtein submodule is disabled, because the optional Levenshtein package <https://pypi.org/project/python-Levenshtein/> is unavailable. Install Levenhstein (e.g. `pip install python-Levenshtein`) to suppress this warning.
  warnings.warn(msg)
C:\Users\brady\Anaconda3\lib\site-packages\sklearn\decomposition\online_lda.py:31: DeprecationWarning: `np.float` is a deprecated alias for the builtin `float`. To silence this warning, use `float` by itself. Doing this will not modify any behavior and is safe. If you specifically wanted the numpy scalar type, use `np.float64` here.
Deprecated in NumPy 1.20; for more details and guidance: https://numpy.org/devdocs/relea

In [4]:
###INSERT STOP WORDS AS NEEDED###

In [5]:
#NLTK Stop words
from nltk.corpus import stopwords
stop_words = stopwords.words('english')
#stop_words.extend(['from', 'subject', 're', 'edu', 'use'])

In [6]:
###IMPORT DATA - THIS IS CURRENTLY UGLY BUT WHATEVER###

###try this later:
#import csv
#reviews = [row for row in csv.reader(open('reviews.csv'))]
#print reviews

In [7]:
df = [
"Chronic inflammation is involved in the onset and development of many diseases, including obesity, atherosclerosis, type 2 diabetes, osteoarthritis, autoimmune and degenerative diseases, asthma, periodontitis, and cirrhosis. The inflammation process is mediated by chemokines, cytokines, and different inflammatory cells. Although the molecules and mechanisms that regulate this primary defense mechanism are not fully understood, recent findings offer a putative role of noncoding RNAs, especially microRNAs (miRNAs), in the progression and management of the inflammatory response. These noncoding RNAs are crucial for the stability and maintenance of gene expression patterns that characterize some cell types, tissues, and biologic responses. Several miRNAs, such as miR-126, miR-132, miR-146, miR-155, and miR-221, have emerged as important transcriptional regulators of some inflammation-related mediators. Additionally, little is known about the involvement of long noncoding RNAs, long intergenic noncoding RNAs, and circular RNAs in inflammation-mediated processes and the homeostatic imbalance associated with metabolic disorders. These noncoding RNAs are emerging as biomarkers with diagnosis value, in prognosis protocols, or in the personalized treatment of inflammation-related alterations. In this context, this review summarizes findings in the field, highlighting those noncoding RNAs that regulate inflammation, with emphasis on recognized mediators such as TNF-alpha, IL-1, IL-6, IL-18, intercellular adhesion molecule 1, VCAM-1, and plasminogen activator inhibitor 1. The down-regulation or antagonism of the noncoding RNAs and the administration of exogenous miRNAs could be, in the near future, a promising therapeutic strategy in the treatment of inflammation-related diseases.", 
"Kinetochores are large protein assemblies that connect chromosomes to microtubules of the mitotic and meiotic spindles in order to distribute the replicated genome from a mother cell to its daughters. Kinetochores also control feedback mechanisms responsible for the correction of incorrect microtubule attachments, and for the coordination of chromosome attachment with cell cycle progression. Finally, kinetochores contribute to their own preservation, across generations, at the specific chromosomal loci devoted to host them, the centromeres. They achieve this in most species by exploiting an epigenetic, DNA-sequence-independent mechanism; notable exceptions are budding yeasts where a specific sequence is associated with centromere function. In the last 15 years, extensive progress in the elucidation of the composition of the kinetochore and the identification of various physical and functional modules within its substructure has led to a much deeper molecular understanding of kinetochore organization and the origins of its functional output. Here, we provide a broad summary of this progress, focusing primarily on kinetochores of humans and budding yeast, while highlighting work from other models, and present important unresolved questions for future studies.", 
"Individual animals frequently exhibit repeatable differences from other members of their population, differences now commonly referred to as 'animal personality'. Personality differences can arise, for example, from differences in permanent environmental effects-including parental and epigenetic contributors- and the effect of additive genetic variation. Although several studies have evaluated the heritability of behaviour, less is known about general patterns of heritability and additive genetic variation in animal personality. As overall variation in behaviour includes both the among-individual differences that reflect different personalities and temporary environmental effects, it is possible for personality to be largely genetically influenced even when heritability of behaviour per se is quite low. The relative contribution of additive genetic variation to personality variation can be estimated whenever both repeatability and heritability are estimated for the same data. Using published estimates to address this issue, we found that approximately 52% of animal personality variation was attributable to additive genetic variation. Thus, while the heritability of behaviour is often moderate or low, the heritability of personality is much higher. Our results therefore (i) demonstrate that genetic differences are likely to be a major contributor to variation in animal personality and (ii) support the phenotypic gambit: that evolutionary inferences drawn from repeatability estimates may often be justified.", 
"Cytosine DNA methylation (mC) is a genome modification that can regulate the expression of coding and non-coding genetic elements. However, little is known about the involvement of mC in response to environmental cues. Using whole genome bisulfite sequencing to assess the spatio-temporal dynamics of mC in rice grown under phosphate starvation and recovery conditions, we identified widespread phosphate starvation-induced changes in mC, preferentially localized in transposable elements (TEs) close to highly induced genes. These changes in mC occurred after changes in nearby gene transcription, were mostly DCL3a-independent, and could partially be propagated through mitosis, however no evidence of meiotic transmission was observed. Similar analyses performed in Arabidopsis revealed a very limited effect of phosphate starvation on mC, suggesting a species-specific mechanism. Overall, this suggests that TEs in proximity to environmentally induced genes are silenced via hypermethylation, and establishes the temporal hierarchy of transcriptional and epigenomic changes in response to stress.", 
"Experience and memory of environmental stimuli that indicate future stress can prepare (prime) organismic stress responses even in species lacking a nervous system. The process through which such organisms prepare their phenotype for an improved response to future stress has been termed 'priming'. however, other terms are also used for this phenomenon, especially when considering priming in different types of organisms and when referring to different stressors. Here we propose a conceptual framework for printing of stress responses in bacteria, fungi and plants winch allows comparison of priming with other terms, e.g. adaptation, acclimation, induction, acquired resistance and cross protection. We address spatial and temporal aspects of priming and highlight current knowledge about the mechanisms necessary for information storage which range from epigenetic marks to the accunmlation of (dormant.) signalling molecules. Furthermore, we outline possible patterns of primed stress responses. Finally, we link the ability of organisms to become primed for stress responses (their 'primability) with evolutionary ecology aspects and discuss which properties of an organism and its environment may favour the evolution of priming of stress responses.", 
"Long noncoding RNAs (lncRNAs) are the major elements of the mammalian transcriptome that is emerging as a central player controlling diverse cellular mechanisms. Most of the well-studied lncRNAs so far are found to be crucial in regulating cellular processes such as cell cycle, growth, and apoptosis that ensure homeostasis. Owing to their location and distribution in the genome, lncRNAs influence the transcription of a wide range of proteins directly or indirectly by transcriptional and posttranscriptional alterations, which opens up the LncRNA-cancer paradigm in a context-dependent manner, i.e., either oncogenic or tumor suppressive. Thus, this chapter is a consolidation of lncRNA association in exhibiting or suppressing the typical cancer hallmarks such as continuous proliferation, surpassing apoptosis, genomic instability, drug resistance, invasion, and metastasis studied till date. In addition, special focus has been given on the efficient application of lncRNAs as potential targets for therapeutics that holds a great promise for future cancer therapy.", 
"Inducible epigenetic changes in eukaryotes are believed to enable rapid adaptation to environmental fluctuations. We have found distinct regions of the Arabidopsis genome that are susceptible to DNA (de)methylation in response to hyperosmotic stress. The stress-induced epigenetic changes are associated with conditionally heritable adaptive phenotypic stress responses. However, these stress responses are primarily transmitted to the next generation through the female lineage due to widespread DNA glycosylase activity in the male germline, and extensively reset in the absence of stress. Using the CNI1/ATL31 locus as an example, we demonstrate that epigenetically targeted sequences function as distantly-acting control elements of antisense long non-coding RNAs, which in turn regulate targeted gene expression in response to stress. Collectively, our findings reveal that plants use a highly dynamic maternal 'short-term stress memory' with which to respond to adverse external conditions. This transient memory relies on the DNA methylation machinery and associated transcriptional changes to extend the phenotypic plasticity accessible to the immediate offspring.", 
"Environmental toxicants can alter epigenetic regulatory features such as DNA methylation and microRNA expression. As the sensitivity of epigenomic regulatory features may be greatest during the in utero period, when critical windows are narrow, and when epigenomic profiles are being set, this review will highlight research focused on that period. I will focus on work in human populations, where the impact of environmental toxicants in utero, including cigarette smoke and toxic trace metals such as arsenic, mercury and manganese, on genome-wide, gene-specific DNA methylation has been assessed. In particular, arsenic is highlighted, as this metalloid has been the focus of a number of studies and its detoxification mechanisms are well understood. Importantly, the tissues and cells being examined must be considered in context in order to interpret the findings of these studies. For example, by studying the placenta, it is possible to identify potential epigenetic adaptations of key genes and pathways that may alter the developmental course in line with the developmental origins of health and disease paradigm. Alternatively, studies of newborn cord blood can be used to examine how environmental exposure in utero can impact the composition of cells within the peripheral blood, leading to immunological effects of exposure. The results suggest that in humans, like other vertebrates, there is a susceptibility for epigenomic alteration by the environment during intrauterine development, and this may represent a mechanism of plasticity of the organism in response to its environment as well as a mechanism through which long-term health consequences can be shaped.", 
"For the last four decades, we have known that noncoding RNAs maintain critical housekeeping functions such as transcription, RNA processing, and translation. However, in the late 1990s and early 2000s, the advent of high-throughput sequencing technologies and computational tools to analyze these large sequencing datasets facilitated the discovery of thousands of small and long noncoding RNAs (lncRNAs) and their functional role in diverse biological functions. For example, lncRNAs have been shown to regulate dosage compensation, genomic imprinting, pluripotency, cell differentiation and development, immune response, etc. Here we review how lncRNAs bring about such copious functions by employing diverse mechanisms such as translational inhibition, mRNA degradation, RNA decoys, facilitating recruitment of chromatin modifiers, regulation of protein activity, regulating the availability of miRNAs by sponging mechanism, etc. In addition, we provide a detailed account of different mechanisms as well as general principles by which lncRNAs organize functionally different nuclear sub-compartments and their impact on nuclear architecture.", 
"The recent and rapid worldwide increase in non-communicable diseases challenges the assumption that genetic factors are the primary contributors to such diseases. A new concept of the 'developmental origins of health and disease' (DOHaD) is at stake and therefore requires a paradigm shift. Maternal obesity and malnutrition predispose offspring to develop metabolic syndrome, a vicious cycle leading to transmission to subsequent generation(s), with differences in response and susceptibility according to the sex of the individual. The placenta is a programming agent of adult health and disease. Adaptations of placental phenotype in response to maternal diet and metabolic status alter fetal nutrient supply. This implies important epigenetic changes that are, however, still poorly documented in DOHaD studies, particularly concerning overnutrition. The aim of this review is to discuss the emerging knowledge on the relationships between the effect of maternal nutrition or metabolic status on placental function and the risk of diseases later in life, with a specific focus on epigenetic mechanisms and sexual dimorphism. Explaining the sex-specific causal variables and how males versus females respond and adapt to environmental perturbations should help physicians and patients to anticipate disease susceptibility.", 
"DNA methylation is extensively remodeled during mammalian gametogenesis and embryogenesis. Most transposons become hypomethylated, raising the question of their regulation in the absence of DNA methylation. To reproduce a rapid and extensive demethylation, we subjected mouse ES cells to chemically defined hypomethylating culture conditions. Surprisingly, we observed two phases of transposon regulation. After an initial burst of de-repression, various transposon families were efficiently re-silenced. This was accompanied by a reconfiguration of the repressive chromatin landscape: while H3K9me3 was stable, H3K9me2 globally disappeared and H3K27me3 accumulated at transposons. Interestingly, we observed that H3K9me3 and H3K27me3 occupy different transposon families or different territories within the same family, defining three functional categories of adaptive chromatin responses to DNA methylation loss. Our work highlights that H3K9me3 and, most importantly, polycomb-mediated H3K27me3 chromatin pathways can secure the control of a large spectrum of transposons in periods of intense DNA methylation change, ensuring longstanding genome stability.", 
"Coral reefs are globally threatened by climate change-related ocean warming and ocean acidification (OA). To date, slow-response mechanisms such as genetic adaptation have been considered the major determinant of coral reef persistence, with little consideration of rapid-response acclimatization-mechanisms. These rapid mechanisms such as parental effects that can contribute to trans-generational acclimatization (e.g. epigenetics) have, however, been identified as important contributors to offspring response in other systems. We present the first evidence of parental effects in a cross-generational exposure to temperature and OA in reef-building corals. Here, we exposed adults to high (28.9 degrees C, 805 mu atm P-CO2) or ambient (26.5 degrees C, 417 mu atm P-CO2) temperature and OA treatments during the larval brooding period. Exposure to high treatment negatively affected adult performance, but their larvae exhibited size differences and metabolic acclimation when subsequently re-exposed, unlike larvae from parents exposed to ambient conditions. Understanding the innate capacity corals possess to respond to current and future climatic conditions is essential to reef protection and maintenance. Our results identify that parental effects may have an important role through (1) ameliorating the effects of stress through preconditioning and adaptive plasticity, and/or (2) amplifying the negative parental response through latent effects on future life stages. Whether the consequences of parental effects and the potential for trans-generational acclimatization are beneficial or maladaptive, our work identifies a critical need to expand currently proposed climate change outcomes for corals to further assess rapid response mechanisms that include non-genetic inheritance through parental contributions and classical epigenetic mechanisms.", 
"Purpose: To review the data concerning the role of endogenously generated reactive oxygen species (ROS) in the non-targeted ionizing radiation (IR) effects and in determination of the cell population's fate, both early after exposure and after many generations. Conclusions: The short-term as well as chronic oxidative stress responses mainly are produced due to ROS generation by the electron transport chain (ETC) of the mitochondria and by the cytoplasmic NADPH oxidases. Whether the induction of the oxidative stress and its consequences occur or are hampered in a single cell largely depends on the interaction between the nucleus and the cellular population of several hundred or thousands of mitochondria that are genetically heterogeneous. High intra-mitochondrial ROS level is damaging the mitochondrial (mt) DNA and its mutations affect the epigenetic control mechanisms of the nuclear (n) DNA, by decreasing the activity of methyltransferases and thus, causing global DNA hypomethylation. These changes are transmitted to the progeny of the irradiated cells. The chronic oxidative stress is the main cause of the late post-radiation effects, including cancer, and this makes it an important adverse effect of exposure to IR and a target for radiological protection.", 
"For many animals, survival of severe environmental stress (e. g. to extremes of heat or cold, drought, oxygen limitation, food deprivation) is aided by entry into a hypometabolic state. Strong depression of metabolic rate, often to only 1-20% of normal resting rate, is a core survival strategy of multiple forms of hypometabolism across the animal kingdom, including hibernation, anaerobiosis, aestivation and freeze tolerance. Global biochemical controls are needed to suppress and reprioritize energy use; one such well-studied control is reversible protein phosphorylation. Recently, we turned our attention to the idea that mechanisms previously associated mainly with epigenetic regulation can also contribute to reversible suppression of gene expression in hypometabolic states. Indeed, situations as diverse as mammalian hibernation and turtle anoxia tolerance show coordinated changes in histone post-translational modifications (acetylation, phosphorylation) and activities of histone deacetylases, consistent with their use as mechanisms for suppressing gene expression during hypometabolism. Other potential mechanisms of gene silencing in hypometabolic states include altered expression of miRNAs that can provide post-transcriptional suppression of mRNA translation and the formation of ribonuclear protein bodies in the nucleus and cytoplasm to allow storage of mRNA transcripts until animals rouse themselves again. Furthermore, mechanisms first identified in epigenetic regulation (e.g. protein acetylation) are now proving to apply to many central metabolic enzymes (e.g. lactate dehydrogenase), suggesting a new layer of regulatory control that can contribute to coordinating the depression of metabolic rate.", 
"Recombination, the exchange of DNA between maternal and paternal chromosomes during meiosis, is an essential feature of sexual reproduction in nearly all multicellular organisms. While the role of recombination in the evolution of sex has received theoretical and empirical attention, less is known about how recombination rate itself evolves and what influence this has on evolutionary processes within sexually reproducing organisms. Here, we explore the patterns of, and processes governing recombination in eukaryotes. We summarize patterns of variation, integrating current knowledge with an analysis of linkage map data in 353 organisms. We then discuss proximate and ultimate processes governing recombination rate variation and consider how these influence evolutionary processes. Genome-wide recombination rates (cM/Mb) can vary more than tenfold across eukaryotes, and there is large variation in the distribution of recombination events across closely related taxa, populations and individuals. We discuss how variation in rate and distribution relates to genome architecture, genetic and epigenetic mechanisms, sex, environmental perturbations and variable selective pressures. There has been great progress in determining the molecular mechanisms governing recombination, and with the continued development of new modelling and empirical approaches, there is now also great opportunity to further our understanding of how and why recombination rate varies. This article is part of the themed issue 'Evolutionary causes and consequences of recombination rate variation in sexual organisms'.", 
"In recent years, the bidirectional communication between the gut microbiome and the brain has emerged as a factor that influences immunity, metabolism, neurodevelopment and behaviour. Cross-talk between the gut and brain begins early in life immediately following the transition from a sterile in utero environment to one that is exposed to a changing and complex microbial milieu over a lifetime. Once established, communication between the gut and brain integrates information from the autonomic and enteric nervous systems, neuroendocrine and neuroimmune signals, and peripheral immune and metabolic signals. Importantly, the composition and functional potential of the gut microbiome undergoes many transitions that parallel dynamic periods of brain development and maturation for which distinct sex differences have been identified. Here, we discuss the sexually dimorphic development, maturation and maintenance of the gut microbiome-brain axis, and the sex differences therein important in disease risk and resilience throughout the lifespan.", 
"Aicardi-Goutieres syndrome (AGS) is a severe childhood inflammatory disorder that shows clinical and genetic overlap with systemic lupus erythematosus (SLE). AGS is thought to arise from the accumulation of incompletely metabolized endogenous nucleic acid species owing to mutations in nucleic acid-degrading enzymes TREX1 (AGS1), RNase H2 (AGS2, 3 and 4), and SAMHD1 (AGS5). However, the identity and source of such immunogenic nucleic acid species remain undefined. Using genome-wide approaches, we show that fibroblasts from AGS patients with AGS1-5 mutations are burdened by excessive loads of RNA: DNA hybrids. Using MethylC-seq, we show that AGS fibroblasts display pronounced and global loss of DNA methylation and demonstrate that AGS-specific RNA: DNA hybrids often occur within DNA hypomethylated regions. Altogether, our data suggest that RNA: DNA hybrids may represent a common immunogenic form of nucleic acids in AGS and provide the first evidence of epigenetic perturbations in AGS, furthering the links between AGS and SLE.", 
"The field described as 'epigenetics' has captured the imagination of scientists and the lay public. Advances in our understanding of chromatin and gene regulatory mechanisms have had impact on drug development, fueling excitement in the lay public about the prospects of applying this knowledge to address health issues. However, when describing these scientific advances as 'epigenetic', we encounter the problem that this term means different things to different people, starting within the scientific community and amplified in the popular press. To help researchers understand some of the misconceptions in the field and to communicate the science accurately to each other and the lay audience, here we review the basis for many of the assumptions made about what are currently referred to as epigenetic processes.", 
"The host innate immune response mediated by type I interferon (IFN) and the resulting up-regulation of hundreds of interferon-stimulated genes (ISGs) provide an immediate barrier to virus infection. Studies of the type I 'interferome' have mainly been carried out at a single species level, often lacking the power necessary to understand key evolutionary features of this pathway. Here, using a single experimental platform, we determined the properties of the interferomes of multiple vertebrate species and developed a webserver to mine the dataset. This approach revealed a conserved 'core' of 62 ISGs, including genes not previously associated with IFN, underscoring the ancestral functions associated with this antiviral host response. We show that gene expansion contributes to the evolution of the IFN system and that interferomes are shaped by lineage-specific pressures. Consequently, each mammal possesses a unique repertoire of ISGs, including genes common to all mammals and others unique to their specific species or phylogenetic lineages. An analysis of genes commonly down-regulated by IFN suggests that epigenetic regulation of transcription is a fundamental aspect of the IFN response. Our study provides a resource for the scientific community highlighting key paradigms of the type I IFN response.", 
"Epigenetics plays an important role in orchestrating key biologic processes. Epigenetic marks, including DNA methylation, histones, chromatin structure, and noncoding RNAs, are modified throughout life in response to environmental and behavioral influences. With each new generation, DNA methylation patterns are erased in gametes and reset after fertilization, probably to prevent these epigenetic marks from being transferred from parents to their offspring. However, some recent animal studies suggest an apparent resistance to complete erasure of epigenetic marks during early development, enabling transgenerational epigenetic inheritance. Whether there are similar mechanisms in humans remains unclear, with the exception of epigenetic imprinting. Nevertheless, a distinctly different mechanism-namely, intrauterine exposure to environmental stressors that may affect establishment of the newly composing epigenetic patterns after fertilization-is often confused with transgenerational epigenetic inheritance. In this review, we delineate the definition of and requirement for transgenerational epigenetic inheritance, differentiate it from the consequences of intrauterine exposure, and discuss the available evidence in both animal models and humans.", 
"In flowering plants, seed development is initiated by the fusion of the maternal egg and central cells with two paternal sperm cells, leading to the formation of embryo and endosperm, respectively. The fertilization products are surrounded by the maternally derived seed coat, whose development prior to fertilization is blocked by epigenetic regulators belonging to the Polycomb Group (PcG) protein family. Here we show that fertilization of the central cell results in the production of auxin and most likely its export to the maternal tissues, which drives seed coat development by removing PcG function. We furthermore show that mutants for the MADS-box transcription factor AGL62 have an impaired transport of auxin from the endosperm to the integuments, which results in seed abortion. We propose that AGL62 regulates auxin transport from the endosperm to the integuments, leading to the removal of the PcG block on seed coat development.", 
"Identifying the genetic input for fetal growth will help to understand common, serious complications of pregnancy such as fetal growth restriction. Genomic imprinting is an epigenetic process that silences one parental allele, resulting in monoallelic expression. Imprinted genes are important in mammalian fetal growth and development. Evidence has emerged showing that genes that are paternally expressed promote fetal growth, whereas maternally expressed genes suppress growth. We have assessed whether the expression levels of key imprinted genes correlate with fetal growth parameters during pregnancy, either early in gestation, using chorionic villus samples (CVS), or in term placenta. We have found that the expression of paternally expressing insulin-like growth factor 2 (IGF2), its receptor IGF2R, and the IGF2/IGF1R ratio in CVS tissues significantly correlate with crown-rump length and birthweight, whereas term placenta expression shows no correlation. For the maternally expressing pleckstrin homology-like domain family A, member 2 (PHLDA2), there is no correlation early in pregnancy in CVS but a highly significant negative relationship in term placenta. Analysis of the control of imprinted expression of PHLDA2 gave rise to a maternally and compounded grand-maternally controlled genetic effect with a birthweight increase of 93/155 g, respectively, when one copy of the PHLDA2 promoter variant is inherited. Expression of the growth factor receptor-bound protein 10 (GRB10) in term placenta is significantly negatively correlated with head circumference. Analysis of the paternally expressing delta-like 1 homologue (DLK1) shows that the paternal transmission of type 1 diabetes protective G allele of rs941576 single nucleotide polymorphism (SNP) results in significantly reduced birth weight (2132 g). In conclusion, we have found that the expression of key imprinted genes show a strong correlation with fetal growth and that for both genetic and genomics data analyses, it is important not to overlook parent-of-origin effects.", 
"Aging is a major risk factor in many forms of late-onset neurodegenerative disorders. The ability to recapitulate age-related characteristics of human neurons in culture will offer unprecedented opportunities to study the biological processes underlying neuronal aging. Here, we show that using a recently demonstrated microRNA-based cellular reprogramming approach, human fibroblasts from postnatal to near centenarian donors can be efficiently converted into neurons that maintain multiple age-associated signatures. Application of an epigenetic biomarker of aging (referred to as epigenetic clock) to DNA methylation data revealed that the epigenetic ages of fibroblasts were highly correlated with corresponding age estimates of reprogrammed neurons. Transcriptome and microRNA profiles reveal genes differentially expressed between young and old neurons. Further analyses of oxidative stress, DNA damage and telomere length exhibit the retention of age-associated cellular properties in converted neurons from corresponding fibroblasts. Our results collectively demonstrate the maintenance of age after neuronal conversion.", 
"Mammalian sperm are carriers of not only the paternal genome, but also the paternal epigenome in the forms of DNA methylation, retained histones and noncoding RNAs. Although paternal DNA methylation and histone retention sites have been correlated with protein-coding genes that are critical for preimplantation embryonic development, physiological evidence of an essential role of these epigenetic marks in fertilization and early development remains lacking. Two miRNA clusters consisting of five miRNAs (miR-34b/c and miR-449a/b/c) are present in sperm, but absent in oocytes, and miR-34c has been reported to be essential for the first cleavage division in vitro. Here, we show that both miR-34b/c- and miR-449-null male mice displayed normal fertility, and that intracytoplasmic injection of either miR-34b/c- or miR-449-null sperm led to normal fertilization, normal preimplantation development and normal birth rate. However, miR-34b/c and miR-449 double knockout (miR-dKO) males were infertile due to severe spermatogenic disruptions and oligo-astheno-teratozoospermia. Injection of miR-dKO sperm into wild-type oocytes led to a block at the two-pronucleus to zygote transition, whereas normal preimplantation development and healthy pups were obtained through injection of miR-dKO round spermatids. Our data demonstrate that miR-34b/c and miR-449a/b/c are essential for normal spermatogenesis and male fertility, but their presence in sperm is dispensable for fertilization and preimplantation development.", 
"Epigenetic mechanisms play a pivotal role in the expression of genes and can be influenced by both the quality and quantity of diet. Dietary compounds such as sulforaphane (SFN) found in cruciferous vegetables and epigallocatechin-3-gallate (EGCG) in green tea exhibit the ability to affect various epigenetic mechanisms such as DNA methyltransferase (DNMT) inhibition, histone modifications via histone deacetylase (HDAC), histone acetyltransferase (HAT) inhibition, or noncoding RNA expression. Regulation of these epigenetic mechanisms has been shown to have notable influences on the formation and progression of various neoplasms. We have shown that an epigenetic diet can influence both cellular longevity and carcinogenesis through the modulation of certain key genes that encode telomerase and p16. Caloric restriction (CR) can also play a crucial role in aging and cancer. Reductions in caloric intake have been shown to increase both the life- and health-span in a variety of animal models. Moreover, restriction of glucose has been demonstrated to decrease the incidence of age-related diseases such as cancer and diabetes. A diet rich in compounds such as genistein, SFN and EGCG can positively modulate the epigenome and lead to many health benefits. Also, reducing the quantity of calories and glucose in the diet can confer an increased health-span, including reduced cancer incidence.", 
"Telomerase is expressed in early human development and then becomes silenced in most normal tissues. Because similar to 90% of primary human tumors express telomerase and generally maintain very short telomeres, telomerase is carefully regulated, particularly in large, long-lived mammals. In the current report, we provide substantial evidence for a new regulatory control mechanism of the rate limiting catalytic protein component of telomerase (hTERT) that is determined by the length of telomeres. We document that normal, young human cells with long telomeres have a repressed hTERT epigenetic status (chromatin and DNA methylation), but the epigenetic status is altered when telomeres become short. The change in epigenetic status correlates with altered expression of TERT and genes near to TERT, indicating a change in chromatin. Furthermore, we identified a chromosome 5p telomere loop to a region near TERT in human cells with long telomeres that is disengaged with increased cell divisions as telomeres progressively shorten. Finally, we provide support for a role of the TRF2 protein, and possibly TERRA, in the telomere looping maintenance mechanism through interactions with interstitial TTAGGG repeats. This provides new insights into how the changes in genome structure during replicative aging result in an increased susceptibility to age-related diseases and cancer prior to the initiation of a DNA damage signal.", 
"Variation in the presence or absence of transposable elements (TEs) is a major source of genetic variation between individuals. Here, we identified 23,095 TE presence/absence variants between 216 Arabidopsis accessions. Most TE variants were rare, and we find these rare variants associated with local extremes of gene expression and DNA methylation levels within the population. Of the common alleles identified, two thirds were not in linkage disequilibrium with nearby SNPs, implicating these variants as a source of novel genetic diversity. Many common TE variants were associated with significantly altered expression of nearby genes, and a major fraction of inter-accession DNA methylation differences were associated with nearby TE insertions. Overall, this demonstrates that TE variants are a rich source of genetic diversity that likely plays an important role in facilitating epigenomic and transcriptional differences between individuals, and indicates a strong genetic basis for epigenetic variation.", 
"Social insects are promising model systems for epigenetics due to their immense morphological and behavioral plasticity. Reports that DNA methylation differs between the queen and worker castes in social insects [1-4] have implied a role for DNA methylation in regulating division of labor. To better understand the function of DNA methylation in social insects, we performed whole-genome bisulfite sequencing on brains of the clonal raider ant Cerapachys biroi, whose colonies alternate between reproductive (queen-like) and brood care (workerlike) phases [5]. Many cytosines were methylated in all replicates (on average 29.5% of the methylated cytosines in a given replicate), indicating that a large proportion of the C. biroi brain methylome is robust. Robust DNA methylation occurred preferentially in exonic CpGs of highly and stably expressed genes involved in core functions. Our analyses did not detect any differences in DNA methylation between the queen-like and worker-like phases, suggesting that DNA methylation is not associated with changes in reproduction and behavior in C. biroi. Finally, many cytosines were methylated in one sample only, due to either biological or experimental variation. By applying the statistical methods used in previous studies [1-4, 6] to our data, we show that such sample-specific DNA methylation may underlie the previous findings of queen-and worker-specific methylation. We argue that there is currently no evidence that genome-wide variation in DNA methylation is associated with the queen and worker castes in social insects, and we call for a more careful interpretation of the available data.", 
"Environmental stresses experienced by individual parents can influence offspring phenotypes in ways that enhance survival under similar conditions. Although such adaptive transgenerational plasticity is well documented, its transmission mechanisms are generally unknown. One possible mechanism is environmentally induced DNA methylation changes. We tested this hypothesis in the annual plant Polygonum persicaria, a species known to express adaptive transgenerational plasticity in response to parental drought stress. Replicate plants of 12 genetic lines (sampled from natural populations) were grown in dry versus moist soil. Their offspring were exposed to the demethylating agent zebularine or to control conditions during germination and then grown in dry soil. Under control germination conditions, the offspring of drought-stressed parents grew longer root systems and attained greater biomass compared with offspring of well-watered parents of the same genetic lines. Demethylation removed these adaptive developmental effects of parental drought, but did not significantly alter phenotypic expression in offspring of well-watered parents. The effect of demethylation on the expression of the parental drought effect varied among genetic lines. Differential seed provisioning did not contribute to the effect of parental drought on offspring phenotypes. These results demonstrate that DNA methylation can mediate adaptive, genotype-specific effects of parental stress on offspring phenotypes.", 
"Since the detection of cell-free DNA (cfDNA) in human plasma in 1948, it has been investigated as a non-invasive screening tool for many diseases, especially solid tumours and foetal genetic abnormalities. However, to date our lack of knowledge regarding the origin and purpose of cfDNA in a physiological environment has limited its use to more obvious diagnostics, neglecting, for example, its potential utility in the identification of predisposition to disease, earlier detection of cancers, and lifestyle-induced epigenetic changes. Moreover, the concept or mechanism of cfDNA could also have potential therapeutic uses such as in immuno- or gene therapy. This review presents an extensive compilation of the putative origins of cfDNA and then contrasts the contributions of cellular breakdown processes with active mechanisms for the release of cfDNA into the extracellular environment. The involvement of cfDNA derived from both cellular breakdown and active release in lateral information transfer is also discussed. We hope to encourage researchers to adopt a more holistic view of cfDNA research, taking into account all the biological pathways in which cfDNA is involved, and to give serious consideration to the integration of in vitro and in vivo research. We also wish to encourage researchers not to limit their focus to the apoptotic or necrotic fraction of cfDNA, but to investigate the intercellular messaging capabilities of the actively released fraction of cfDNA and to study the role of cfDNA in pathogenesis.", 
"The role of natural selection in the evolution of adaptive phenotypes has undergone constant probing by evolutionary biologists, employing both theoretical and empirical approaches. As Darwin noted, natural selection can act together with other processes, including random changes in the frequencies of phenotypic differences that are not under strong selection, and changes in the environment, which may reflect evolutionary changes in the organisms themselves. As understanding of genetics developed after 1900, the new genetic discoveries were incorporated into evolutionary biology. The resulting general principles were summarized by Julian Huxley in his 1942 book Evolution: the modern synthesis. Here, we examine how recent advances in genetics, developmental biology and molecular biology, including epigenetics, relate to today's understanding of the evolution of adaptations. We illustrate how careful genetic studies have repeatedly shown that apparently puzzling results in a wide diversity of organisms involve processes that are consistent with neo-Darwinism. They do not support important roles in adaptation for processes such as directed mutation or the inheritance of acquired characters, and therefore no radical revision of our understanding of the mechanism of adaptive evolution is needed.", 
"Genomic imprinting is an epigenetic phenomenon causing parent-of-origin specific differential expression of maternally and paternally inherited alleles. While many imprinted genes have been identified in plants, the functional roles of most of them are unknown. In this study, we systematically examine the functional requirement of paternally expressed imprinted genes (PEGs) during seed development in Arabidopsis thaliana. While none of the 15 analyzed peg mutants has qualitative or quantitative abnormalities of seed development, we identify three PEGs that establish postzygotic hybridization barriers in the endosperm, revealing that PEGs have a major role as speciation genes in plants. Our work reveals that a subset of PEGs maintains functional roles in the inbreeding plant Arabidopsis that become evident upon deregulated expression.", 
"LINE-1 (L1) retrotransposons represent approximately one sixth of the human genome, but only the human-specific L1HS-Ta subfamily acts as an endogenous mutagen in modern humans, reshaping both somatic and germline genomes. Due to their high levels of sequence identity and the existence of many polymorphic insertions absent from the reference genome, the transcriptional activation of individual genomic L1HS-Ta copies remains poorly understood. Here we comprehensively mapped fixed and polymorphic L1HS-Ta copies in 12 commonly-used somatic cell lines, and identified transcriptional and epigenetic signatures allowing the unambiguous identification of active L1HS-Ta copies in their genomic context. Strikingly, only a very restricted subset of L1HS-Ta loci - some being polymorphic among individuals - significantly contributes to the bulk of L1 expression, and these loci are differentially regulated among distinct cell lines. Thus, our data support a local model of L1 transcriptional activation in somatic cells, governed by individual-, locus-, and cell-type-specific determinants.", 
"Two parallel pathways produce cholesterol: the Bloch and Kandutsch-Russell pathways. Here we used stable isotope labeling and isotopomer analysis to trace sterol flux through the two pathways in mice. Surprisingly, no tissue used the canonical K-R pathway. Rather, a hybrid pathway was identified that we call the modified K-R (MK-R) pathway. Proportional flux through the Bloch pathway varied from 8% in preputial gland to 97% in testes, and the tissue-specificity observed in vivo was retained in cultured cells. The distribution of sterol isotopomers in plasma mirrored that of liver. Sterol depletion in cultured cells increased flux through the Bloch pathway, whereas overexpression of 24-dehydrocholesterol reductase (DHCR24) enhanced usage of the MK-R pathway. Thus, relative use of the Bloch and MK-R pathways is highly variable, tissue-specific, flux dependent, and epigenetically fixed. Maintenance of two interdigitated pathways permits production of diverse bioactive sterols that can be regulated independently of cholesterol.", 
"The number of children born since the origin of Assisted Reproductive Technologies (ART) exceeds 5 million. The majority seem healthy, but a higher frequency of defects has been reported among ART-conceived infants, suggesting an epigenetic cost. We report the first wholegenome DNA methylation datasets from single pig blastocysts showing differences between in vivo and in vitro produced embryos. Blastocysts were produced in vitro either without (C-IVF) or in the presence of natural reproductive fluids (Natur-IVF). Natur-IVF embryos were of higher quality than C-IVF in terms of cell number and hatching ability. RNA-Seq and DNA methylation analyses showed that Natur-IVF embryos have expression and methylation patterns closer to in vivo blastocysts. Genes involved in reprogramming, imprinting and development were affected by culture, with fewer aberrations in Natur-IVF embryos. Methylation analysis detected methylated changes in C-IVF, but not in Natur-IVF, at genes whose methylation could be critical, such as IGF2R and NNAT.", 
"Upon fertilization, the highly specialised sperm and oocyte genomes are remodelled to confer totipotency. The mechanisms of the dramatic reprogramming events that occur have remained unknown, and presumed roles of histone modifying enzymes are just starting to be elucidated. Here, we explore the function of the oocyte-inherited pool of a histone H3K4 and K9 demethylase, LSD1/KDM1A during early mouse development. KDM1A deficiency results in developmental arrest by the two-cell stage, accompanied by dramatic and stepwise alterations in H3K9 and H3K4 methylation patterns. At the transcriptional level, the switch of the maternal-to-zygotic transition fails to be induced properly and LINE-1 retrotransposons are not properly silenced. We propose that KDM1A plays critical roles in establishing the correct epigenetic landscape of the zygote upon fertilization, in preserving genome integrity and in initiating new patterns of genome expression that drive early mouse development.", 
"DNA methylation regulates many cellular processes, including embryonic development, transcription, chromatin structure, X-chromosome inactivation, genomic imprinting and chromosome stability. DNA methyltransferases establish and maintain the presence of 5-methylcytosine (5mC), and ten-eleven translocation cytosine dioxygenases (TETs) oxidise 5mC to 5-hydroxymethylcytosine (5hmC), 5-formylcytosine (5fC) and 5-carboxylcytosine (5caC), which can be removed by base excision repair (BER) proteins. Multiple forms of DNA methylation are recognised by methyl-CpG binding proteins (MeCPs), which play vital roles in chromatin-based transcriptional regulation, DNA repair and replication. Accordingly, defects in DNA methylation and its mediators may cause silencing of tumour suppressor genes and misregulation of multiple cell cycles, DNA repair and chromosome stability genes, and hence contribute to genome instability in various human diseases, including cancer. Thus, understanding functional genetic mutations and aberrant expression of these DNA methylation mediators is critical to deciphering the crosstalk between concurrent genetic and epigenetic alterations in specific cancer types and to the development of new therapeutic strategies.", 
"Ten-eleven translocation (TET) enzymes oxidize 5-methylcytosine, facilitating DNA demethylation and generating new epigenetic marks. Here we show that concomitant loss of Tet2 and Tet3 in mice at early B cell stage blocked the pro- to pre-B cell transition in the bone marrow, decreased Irf4 expression and impaired the germline transcription and rearrangement of the Ig kappa locus. Tet2/3-deficient pro-B cells showed increased CpG methylation at the Ig kappa 3' and distal enhancers that was mimicked by depletion of E2A or PU.1, as well as a global decrease in chromatin accessibility at enhancers. Importantly, re-expression of the Tet2 catalytic domain in Tet2/3-deficient B cells resulted in demethylation of the Igx enhancers and restored their chromatin accessibility. Our data suggest that TET proteins and lineage-specific transcription factors cooperate to influence chromatin accessibility and Igx enhancer function by modulating the modification status of DNA.", 
"Group-living animals must adjust the expression of their social behaviour to changes in their social environment and to transitions between life-history stages, and this social plasticity can be seen as an adaptive trait that can be under positive selection when changes in the environment outpace the rate of genetic evolutionary change. Here, we propose a conceptual framework for understanding the neuromolecular mechanisms of social plasticity. According to this framework, social plasticity is achieved by rewiring or by biochemically switching nodes of a neural network underlying social behaviour in response to perceived social information. Therefore, at the molecular level, it depends on the social regulation of gene expression, so that different genomic and epigenetic states of this brain network correspond to different behavioural states, and the switches between states are orchestrated by signalling pathways that interface the social environment and the genotype. Different types of social plasticity can be recognized based on the observed patterns of inter- versus intra-individual occurrence, time scale and reversibility. It is proposed that these different types of social plasticity rely on different proximate mechanisms at the physiological, neural and genomic level.", 
"While N-6-methyladenosine (m(6)A) is a well-known epigenetic modification inbacterial DNA, it remained largely unstudied in eukaryotes. Recent studies have brought to fore its potential epigenetic role across diverse eukaryotes with biological consequences, which are distinct and possibly even opposite to the well-studied 5-methylcytosine mark. Adenine methyltransferases appear to have been independently acquired by eukaryotes on at least 13 occasions from prokaryotic restriction-modification and counter-restriction systems. On at least four to five instances, these methyltransferases were recruited as RNA methylases. Thus, m(6)A marks in eukaryotic DNA and RNA might be more wide spread and diversified than previously believed. Several m(6)A-binding protein domains from prokaryotes were also acquired by eukaryotes, facilitating prediction of potential readers for these marks. Further, multiple lineages of the AlkB family of dioxygenases have been recruited as m(6)A demethylases. Although members of the TET/JBP family of dioxygenases have also been suggested to be m(6)A demethylases, this proposal needs more careful evaluation.", 
"N-6-methyladenosine (m(6)A) is a vital post-transcriptional modification, which adds another layer of epigenetic regulation at RNA level. It chemically modifies mRNA that effects protein expression. RNA sequence contains many genetic code motifs (GAC). Among these codes, identification of methylated or not methylated GAC motif is highly indispensable. However, with a large number of RNA sequences generated in post-genomic era, it becomes a challenging task how to accurately and speedily characterize these sequences. In view of this, the concept of an intelligent is incorporated with a computational model that truly and fast reflects the motif of the desired classes. An intelligent computational model iMethyl-STTNC model is proposed for identification of methyladenosine sites in RNA. In the proposed study, four feature extraction techniques, such as; Pseudo-dinucleotide-composition, Pseudo-trinucleotide-composition, split-trinucleotide-composition, and split-tetra-nucleotides-composition (STTNC) are utilized for genuine numerical descriptors. Three different classification algorithms including probabilistic neural network, Support vector machine (SVM), and K-nearest neighbor are adopted for prediction. After examining the outcomes of prediction model on each feature spaces, SVM using STTNC feature space reported the highest accuracy of 69.84%, 91.84% on dataset1 and dataset2, respectively. The reported results show that our proposed predictor has achieved encouraging results compared to the present approaches, so far in the research. It is finally reckoned that our developed model might be beneficial for in-depth analysis of genomes and drug development. (C) 2018 Elsevier Ltd. All rights reserved.", 
"The epigenetic inheritance of DNA methylation requires UHRF1, a histone- and DNA-binding RING E3 ubiquitin ligase that recruits DNMT1 to sites of newly replicated DNA through ubiquitylation of histone H3. UHRF1 binds DNA with selectivity towards hemi-methylated CpGs (HeDNA); however, the contribution of HeDNA sensing to UHRF1 function remains elusive. Here, we reveal that the interaction of UHRF1 with HeDNA is required for DNA methylation but is dispensable for chromatin interaction, which is governed by reciprocal positive cooperativity between the UHRF1 histone- and DNA-binding domains. HeDNA recognition activates UHRF1 ubiquitylation towards multiple lysines on the H3 tail adjacent to the UHRF1 histone-binding site. Collectively, our studies are the first demonstrations of a DNA-protein interaction and an epigenetic modification directly regulating E3 ubiquitin ligase activity. They also define an orchestrated epigenetic control mechanism involving modifications both to histones and DNA that facilitate UHRF1 chromatin targeting, H3 ubiquitylation, and DNA methylation inheritance.", 
"Inheritance of gene expression states is fundamental for cells to 'remember' past events, such as environmental or developmental cues. The conserved Polycomb Repressive Complex 2 (PRC2) maintains epigenetic repression of many genes in animals and plants and modifies chromatin at its targets. Histones modified by PRC2 can be inherited through cell division. However, it remains unclear whether this inheritance can direct long-term memory of individual gene expression states (cis memory) or instead if local chromatin states are dictated by the concentrations of diffusible factors (trans memory). By monitoring the expression of two copies of the Arabidopsis Polycomb target gene FLOWERING LOCUS C (FLC) in the same plants, we show that one copy can be repressed while the other is active. Furthermore, this 'mixed' expression state is inherited through many cell divisions as plants develop. These data demonstrate that epigenetic memory of FLC expression is stored not in trans but in cis.", 
"Loss of polarity correlates with progression of epithelial cancers, but how plasma membrane misorganization drives oncogenic transcriptional events remains unclear. The polarity regulators of the Drosophila Scribble (Scrib) module are potent tumor suppressors and provide a model to investigate these mechanisms. RNA profiling of Scrib module mutant tumors reveals multiple signatures of neoplasia, including altered metabolism and dedifferentiation. A prominent gene expression change is upregulation of the cytokine-like Unpaired (Upd) ligands, which drive tumor overgrowth. We identified a polarity-responsive enhancer in upd3, which is activated in a coincident manner by both JNK-dependent Fos and aPKC-mediated Yki transcription. This enhancer, and Scrib module mutant overgrowth in general, are also sensitive to activity of the Polycomb Group (PcG), suggesting that PcG attenuation upon polarity loss potentiates select targets for activation by JNK and Yki. Our results link epithelial organization to signaling and epigenetic regulators that control tissue repair programs, and provide insight into why epithelial polarity is tumor-suppressive.", 
"One of the most striking patterns of genome structure is the tight, typically negative, association between transposable elements (TEs) and meiotic recombination rates. While this is a highly recurring feature of eukaryotic genomes, the mechanisms driving correlations between TEs and recombination remain poorly understood, and distinguishing cause versus effect is challenging. Here, we review the evidence for a relation between TEs and recombination, and discuss the underlying evolutionary forces. Evidence to date suggests that overall TE densities correlate negatively with recombination, but the strength of this correlation varies across element types, and the pattern can be reversed. Results suggest that heterogeneity in the strength of selection against ectopic recombination and gene disruption can drive TE accumulation in regions of low recombination, but there is also strong evidence that the regulation of TEs can influence local recombination rates. We hypothesize that TE insertion polymorphism may be important in driving within-species variation in recombination rates in surrounding genomic regions. Furthermore, the interaction between TEs and recombination may create positive feedback, whereby TE accumulation in non-recombining regions contributes to the spread of recombination suppression. Further investigation of the coevolution between recombination and TEs has important implications for our understanding of the evolution of recombination rates and genome structure. This article is part of the themed issue 'Evolutionary causes and consequences of recombination rate variation in sexual organisms'.", 
"Organisms can change their physiological/behavioural traits to adapt and survive in changed environments. However, whether these acquired traits can be inherited across generations through non-genetic alterations has been a topic of debate for over a century. Emerging evidence indicates that both ancestral and parental experiences, including nutrition, environmental toxins, nurturing behaviour, and social stress, can have powerful effects on the physiological, metabolic and cellular functions in an organism. In certain circumstances, these effects can be transmitted across several generations through epigenetic (i.e. non-DNA sequence-based rather than mutational) modifications. In this review, we summarize recent evidence on epigenetic inheritance from parental environment-induced developmental and physiological alterations in nematodes, fruit flies, zebrafish, rodents, and humans. The epigenetic modifications demonstrated to be both susceptible to modulation by environmental cues and heritable, including DNA methylation, histone modification, and small non-coding RNAs, are also summarized. We particularly focus on evidence that parental environment-induced epigenetic alterations are transmitted through both the maternal and paternal germlines and exert sex-specific effects. The thought-provoking data presented here raise fundamental questions about the mechanisms responsible for these phenomena. In particular, the means that define the specificity of the response to parental experience in the gamete epigenome and that direct the establishment of the specific epigenetic change in the developing embryos, as well as in specific tissues in the descendants, remain obscure and require elucidation. More precise epigenetic assessment at both the genome-wide level and single-cell resolution as well as strategies for breeding at relatively sensitive periods of development and manipulation aimed at specific epigenetic modification are imperative for identifying parental environment-induced epigenetic marks across generations. Considering their diverse epigenetic architectures, the conservation and prevalence of the mechanisms underlying epigenetic inheritance in non-mammals require further investigation in mammals. Interpretation of the consequences arising from epigenetic inheritance on organisms and a better understanding of the underlying mechanisms will provide insight into how gene-environment interactions shape developmental processes and physiological functions, which in turn may have wide-ranging implications for human health, and understanding biological adaptation and evolution.", 
"In yeast and humans, previous experiences can lead to epigenetic transcriptional memory: repressed genes that exhibit mitotically heritable changes in chromatin structure and promoter recruitment of poised RNA polymerase II preinitiation complex (RNAPII PIC), which enhances future reactivation. Here, we show that INO1 memory in yeast is initiated by binding of the Sfl1 transcription factor to the cis-acting Memory Recruitment Sequence, targeting INO1 to the nuclear periphery. Memory requires a remodeled form of the Set1/COMPASS methyltransferase lacking Spp1, which dimethylates histone H3 lysine 4 (H3K4me2). H3K4me2 recruits the SET3C complex, which plays an essential role in maintaining this mark. Finally, while active INO1 is associated with Cdk8(-) Mediator, during memory, Cdk8(+) Mediator recruits poised RNAPII PIC lacking the Kin28 CTD kinase. Aspects of this mechanism are generalizable to yeast and conserved in human cells. Thus, COMPASS and Mediator are repurposed to promote epigenetic transcriptional poising by a highly conserved mechanism.", 
"The advent of in vitro fertilization (IVF) in animals and humans implies an extraordinary change in the environment where the beginning of a new organism takes place. In mammals fertilization occurs in the maternal oviduct, where there are unique conditions for guaranteeing the encounter of the gametes and the first stages of development of the embryo and thus its future. During this period a major epigenetic reprogramming takes place that is crucial for the normal fate of the embryo. This epigenetic reprogramming is very vulnerable to changes in environmental conditions such as the ones implied in IVF, including in vitro culture, nutrition, light, temperature, oxygen tension, embryo-maternal signaling, and the general absence of protection against foreign elements that could affect the stability of this process. The objective of this review is to update the impact of the various conditions inherent in the use of IVF on the epigenetic profile and outcomes of mammalian embryos, including superovulation, IVF technique, embryo culture and manipulation and absence of embryo-maternal signaling. It also covers the possible transgenerational inheritance of the epigenetic alterations associated with assisted reproductive technologies (ART), including its phenotypic consequences as is in the case of the large offspring syndrome (LOS). Finally, the important scientific and bioethical implications of the results found in animals are discussed in terms of the ART in humans.", 
"Facioscapulohumeral muscular dystrophy (FSHD) is a muscular dystrophy caused by inefficient epigenetic repression of the D4Z4 macrosatellite array and somatic expression of the DUX4 retrogene. DUX4 is a double homeobox transcription factor that is normally expressed in the testis and causes apoptosis and FSHD when mis-expressed in skeletal muscle. The mechanism(s) of DUX4 toxicity in muscle is incompletely understood. We report that DUX4-triggered proteolytic degradation of UPF1, a central component of the nonsense-mediated decay (NMD) machinery, is associated with profound NMD inhibition, resulting in global accumulation of RNAs normally degraded as NMD substrates. DUX4 mRNA is itself degraded by NMD, such that inhibition of NMD by DUX4 protein stabilizes DUX4 mRNA through a double-negative feedback loop in FSHD muscle cells. This feedback loop illustrates an unexpected mode of autoregulatory behavior of a transcription factor, is consistent with bursts of DUX4 expression in FSHD muscle, and has implications for FSHD pathogenesis.", 
"Long noncoding RNAs belong to a class of noncoding RNAs longer than 200 nucleotides with the epigenetic regulation potential. As a novel molecular regulator, IncRNAs are often dysregulated in various pathological conditions and display multiple functions in a wide range of biological processes. Given that recent studies have indicated that IncRNAs are involved in atherosclerosis-related smooth muscle cell, endothelial cell, macrophage and lipid metabolism regulation, it is pertinent to understand the potential function of IncRNAs in atherosclerosis development. This review will highlight the recent updates of IncRNAs in atherogenesis and also discuss their potential roles as novel therapeutic targets.", 
"The H19 gene produces a non-coding RNA, which is abundantly expressed during embryonic development and down-regulated after birth. Although this gene was discovered over 20 years ago, its function has remained unclear. Only recently a role was identified for the non-coding RNA and/or its microRNA partner, first as a tumour suppressor gene in mice, then as a trans-regulator of a group of co-expressed genes belonging to the imprinted gene network that is likely to control foetal and early postnatal growth in mice. The mechanisms underlying this transcriptional or post-transcriptional regulation remain to be discovered, perhaps by identifying the protein partners of the full-ength H19 RNA or the targets of the microRNA. This first in vivo evidence of a functional role for the H19 locus provides new insights into how genomic imprinting helps to control embryonic growth.", 
"Obesity is highly prevalent, and its incidence is increasing. The previous study showing a major effect of paternal obesity on metabolic health of offspring is confounded by comorbidity with diabetes. Therefore, we investigated the effect of diet-induced paternal obesity, in the absence of diabetes, on the metabolic health of two resultant generations and the molecular profiles of the testes and sperm. Founder (F-0) male C57BL6 mice were fed either a high-fat diet (HFD) or a control diet (CD); n = 10/diet for a period of 10 wk. Testis expression of mRNA/microRNAs was analyzed by microarray and qPCR and sperm microRNA abundance by qPCR. Two subsequent generations were generated by mating F-0 and then F-1 mice to CD mice, and their metabolic health was investigated. All mice, other than F-0 males, were maintained on a CD. HFD feeding induced paternal obesity with a 21% increase in adiposity, but not overt diabetes, and initiated intergenerational transmission of obesity and insulin resistance in two generations of offspring. This distinct phenotypic constellation is either partially or fully transmitted to both female and male F-1 offspring and further transmitted through both parental lineages to the F-2 generation, with a heightened effect on female F-1 offspring (+67% in adiposity) and their F-2 sons (+24% in adiposity). Founder male obesity altered the testes expression of 414 mRNAs by microarray and 11 microRNAs by qPCR, concomitant with alterations in sperm microRNA content and a 25% reduction in global methylation of germ cell DNA. Diet-induced paternal obesity modulates sperm microRNA content and germ cell methylation status, which are potential signals that program offspring health and initiate the transmission of obesity and impaired metabolic health to future generations. This study implicates paternal obesity in the transgenerational amplification of obesity and type 2 diabetes in humans.Fullston, T., Ohlsson Teague, E. M. C., Palmer, N. O., DeBlasio, M. J., Mitchell, M., Corbett, M., Print, C. G., Owens, J. A., Lane, M. Paternal obesity initiates metabolic disturbances in two generations of mice with incomplete penetrance to the F-2 generation and alters the transcriptional profile of testis and sperm microRNA content.", 
"CpG islands (CGIs) are associated with most mammalian gene promoters. A subset of CGIs act as polycomb response elements (PREs) and are recognized by the polycomb silencing systems to regulate expression of genes involved in early development. How CGIs function mechanistically as nucleation sites for polycomb repressive complexes remains unknown. Here we discover that KDM2B (FBXL10) specifically recognizes non-methylated DNA in CGIs and recruits the polycomb repressive complex 1 (PRC1). This contributes to histone H2A lysine 119 ubiquitylation (H2AK119ub1) and gene repression. Unexpectedly, we also find that CGIs are occupied by low levels of PRC1 throughout the genome, suggesting that the KDM2B-PRC1 complex may sample CGI-associated genes for susceptibility to polycomb-mediated silencing. These observations demonstrate an unexpected and direct link between recognition of CGIs by KDM2B and targeting of the polycomb repressive system. This provides the basis for a new model describing the functionality of CGIs as mammalian PREs.", 
"In mammalian development, epigenetic modifications, including DNA methylation patterns, play a crucial role in defining cell fate but also represent epigenetic barriers that restrict developmental potential. At two points in the life cycle, DNA methylation marks are reprogrammed on a global scale, concomitant with restoration of developmental potency. DNA methylation patterns are subsequently re-established with the commitment towards a distinct cell fate. This reprogramming of DNA methylation takes place firstly on fertilization in the zygote, and secondly in primordial germ cells (PGCs), which are the direct progenitors of sperm or oocyte. In each reprogramming window, a unique set of mechanisms regulates DNA methylation erasure and re-establishment. Recent advances have uncovered roles for the TET3 hydroxylase and passive demethylation, together with base excision repair (BER) and the elongator complex, in methylation erasure from the zygote. Deamination by AID, BER and passive demethylation have been implicated in reprogramming in PGCs, but the process in its entirety is still poorly understood. In this review, we discuss the dynamics of DNA methylation reprogramming in PGCs and the zygote, the mechanisms involved and the biological significance of these events. Advances in our understanding of such natural epigenetic reprogramming are beginning to aid enhancement of experimental reprogramming in which the role of potential mechanisms can be investigated in vitro. Conversely, insights into in vitro reprogramming techniques may aid our understanding of epigenetic reprogramming in the germline and supply important clues in reprogramming for therapies in regenerative medicine.", 
"DNA methylation is an essential epigenetic mark whose role in gene regulation and its dependency on genomic sequence and environment are not fully understood. In this study we provide novel insights into the mechanistic relationships between genetic variation, DNA methylation and transcriptome sequencing data in three different cell-types of the GenCord human population cohort. We find that the association between DNA methylation and gene expression variation among individuals are likely due to different mechanisms from those establishing methylation-expression patterns during differentiation. Furthermore, cell-type differential DNA methylation may delineate a platform in which local inter-individual changes may respond to or act in gene regulation. We show that unlike genetic regulatory variation, DNA methylation alone does not significantly drive allele specific expression. Finally, inferred mechanistic relationships using genetic variation as well as correlations with TF abundance reveal both a passive and active role of DNA methylation to regulatory interactions influencing gene expression.", 
"The prospect of finding epigenetic risk factors for complex diseases would be greatly enhanced if DNA from existing biobanks, which is generally extracted from whole blood, could be used to perform epigenetic association studies. We characterized features of DNA methylation at 16 candidate loci, 8 of which were imprinted, in DNA samples from the Netherlands Twin Register biobank. Except for un-methylated or fully methylated sites, CpG methylation varied considerably in a sample of 30 unrelated individuals. This variation remained after accounting for the cellular heterogeneity of blood. Methylation of CpG sites was correlated within loci and, for 4 imprinted loci, across chromosomes. In 34 additional individuals, we investigated the DNA methylation of 8 representative loci in 2 longitudinal blood and 2 longitudinal buccal cell samples (follow-up 11-20 and 2-8 yr, respectively). Five of 8 loci were stable over time (rho > 0.75) in both tissues, indicating that prospective epigenetic studies may be possible. For 4 loci, the DNA methylation in blood (mesoderm) correlated with that in the buccal cells (ectoderm) (rho > 0.75). Our data suggest that epigenetic studies on complex diseases may be feasible for a proportion of genomic loci provided that they are carefully designed.-Talens, R. P., Boomsma, D. I., Tobi, E. W., Kremer, D., Jukema, J. W., Willemsen, G., Putter, H., Slagboom, P. E., Heijmans, B. T. Variation, patterns, and temporal stability of DNA methylation: considerations for epigenetic epidemiology. FASEB J. 24, 3135-3144 (2010). www.fasebj.org", 
"Autism is currently considered a multigene disorder with epigenetic influences. To investigate the contribution of DNA methylation to autism spectrum disorders, we have recently completed large-scale methylation profiling by CpG island microarray analysis of lymphoblastoid cell lines derived from monozygotic twins discordant for diagnosis of autism and their nonautistic siblings. Methylation profiling revealed many candidate genes differentially methylated between discordant MZ twins as well as between both twins and nonautistic siblings. Bioinformatics analysis of the differentially methylated genes demonstrated enrichment for high-level functions including gene transcription, nervous system development, cell death/survival, and other biological processes implicated in autism. The methylation status of 2 of these candidate genes, BCL-2 and retinoic acid-related orphan receptor alpha (RORA), was further confirmed by bisulfite sequencing and methylation-specific PCR, respectively. Immunohistochemical analyses of tissue arrays containing slices of the cerebellum and frontal cortex of autistic and age-and sex-matched control subjects revealed decreased expression of RORA and BCL-2 proteins in the autistic brain. Our data thus confirm the role of epigenetic regulation of gene expression via differential DNA methylation in idiopathic autism, and furthermore link molecular changes in a peripheral cell model with brain pathobiology in autism.-Nguyen, A., Rauch, T. A., Pfeifer, G. P., Hu, V. W. Global methylation profiling of lymphoblastoid cell lines reveals epigenetic contributions to autism spectrum disorders and a novel autism candidate gene, RORA, whose protein product is reduced in autistic brain. FASEB J. 24, 3036-3051 (2010). www.fasebj.org", 
"The development of multicellular organisms is controlled by differential gene expression whereby cells adopt distinct fates. A spatially resolved view of gene expression allows the elucidation of transcriptional networks that are linked to cellular identity and function. The haploid female gametophyte of flowering plants is a highly reduced organism: at maturity, it often consists of as few as three cell types derived from a common precursor [1, 2]. However, because of its inaccessibility and small size, we know little about the molecular basis of cell specification and differentiation in the female gametophyte. Here we report expression profiles of all cell types in the mature Arabidopsis female gametophyte. Differentially expressed posttranscriptional regulatory modules and metabolic pathways characterize the distinct cell types. Several transcription factor families are overrepresented in the female gametophyte in comparison to other plant tissues, e.g., type I MADS domain, RWP-RK, and reproductive meristem transcription factors. PAZ/Piwi-domain encoding genes are upregulated in the egg, indicating a role of epigenetic regulation through small RNA pathways a feature paralleled in the germline of animals [3]. A comparison of human and Arabidopsis egg cells for enrichment of functional groups identified several similarities that may represent a consequence of coevolution or ancestral gametic features.", 
"Background: Ant societies comprise individuals belonging to different castes characterized by specialized morphologies and behaviors. Because ant embryos can follow different developmental trajectories, epigenetic mechanisms must play a role in caste determination. Ants have a full set of DNA methyltransferases and their genomes contain methylcytosine. To determine the relationship between DNA methylation and phenotypic plasticity in ants, we obtained and compared the genome-wide methylonnes of different castes and developmental stages of Camponotus floridanus and Harpegnathos saltator. Results: In the ant genomes, methylcytosines are found both in symmetric CG dinucleotides (CpG) and non-CpG contexts and are strongly enriched at exons of active genes. Changes in exonic DNA methylation correlate with alternative splicing events such as exon skipping and alternative splice site selection. Several genes exhibit caste-specific and developmental changes in DNA methylation that are conserved between the two species, including genes involved in reproduction, telomere maintenance, and noncoding RNA metabolism. Several loci are methylated and expressed monoallelically, and in some cases, the choice of methylated allele depends on the caste. Conclusions: These first ant methylomes and their intra- and interspecies comparison reveal an exonic methylation pattern that points to a connection between DNA methylation and splicing. The presence of monoallelic DNA methylation and the methylation of non-CpG sites in all samples suggest roles in genome regulation in these social insects, including the intriguing possibility of parental or caste-specific genomic imprinting.", 
"Polyphenism is the phenomenon where two or more distinct phenotypes are produced by the same genotype. Examples of polyphenism provide some of the most compelling systems for the study of epigenetics. Polyphenisms are a major reason for the success of the insects, allowing them to partition life history stages (with larvae dedicated to feeding and growth, and adults dedicated to reproduction and dispersal), to adopt different phenotypes that best suit predictable environmental changes (seasonal morphs), to cope with temporally heterogeneous environments (dispersal morphs), and to partition labour within social groups (the castes of eusocial insects). We survey the status of research on some of the best known examples of insect polyphenism, in each case considering the environmental cues that trigger shifts in phenotype, the neurochemical and hormonal pathways that mediate the transformation, the molecular genetic and epigenetic mechanisms involved in initiating and maintaining the polyphenism, and the adaptive and life-history significance of the phenomenon. We conclude by highlighting some of the common features of these examples and consider future avenues for research on polyphenism.", 
"New DNA sequencing technologies have provided novel insights into eukaryotic genomes, epigenomes, and the transcriptome, including the identification of new non-coding RNA (ncRNA) classes such as promoter-associated RNAs and long RNAs. Moreover, it is now clear that up to 90% of eukaryotic genomes are transcribed, generating an extraordinary range of RNAs with no coding capacity. Taken together, these new discoveries are modifying the status quo in genomic science by demonstrating that the eukaryotic gene pool is divided into two distinct categories of transcripts: protein-coding and non-coding. The function of the majority of ncRNAs produced by the transcriptome is largely unknown; however, it is probable that many are associated with epigenetic mechanisms. The purpose of this review is to describe the most recent discoveries in the ncRNA field that implicate these molecules as key players in the epigenome.", 
"Literature on maternal exposures and the risk of epigenetic changes or diseases in the offspring is growing. Paternal contributions are often not considered. However, some animal and epidemiologic studies on various contaminants, nutrition, and lifestyle-related conditions suggest a paternal influence on the offspring's future health. The phenotypic outcomes may have been attributed to DNA damage or mutations, but increasing evidence shows that the inheritance of environmentally induced functional changes of the genome, and related disorders, are (also) driven by epigenetic components. In this essay we suggest the existence of epigenetic windows of susceptibility to environmental insults during sperm development. Changes in DNA methylation, histone modification, and non-coding RNAs are viable mechanistic candidates for a non-genetic transfer of paternal environmental information, from maturing germ cell to zygote. Inclusion of paternal factors in future research will ultimately improve the understanding of transgenerational epigenetic plasticity and health-related effects in future generations.", 
"DNA methylation, especially CpG methylation at promoter regions, has been generally considered as a potent epigenetic modification that prohibits transcription factor (TF) recruitment, resulting in transcription suppression. Here, we used a protein microarray-based approach to systematically survey the entire human TF family and found numerous purified TFs with methylated CpG (mCpG)-dependent DNA-binding activities. Interestingly, some TFs exhibit specific binding activity to methylated and unmethylated DNA motifs of distinct sequences. To elucidate the underlying mechanism, we focused on Kruppel-like factor 4 (KLF4), and decoupled its mCpG- and CpG-binding activities via site-directed mutagenesis. Furthermore, KLF4 binds specific methylated or unmethylated motifs in human embryonic stem cells in vivo. Our study suggests that mCpG-dependent TF binding activity is a widespread phenomenon and provides a new framework to understand the role and mechanism of TFs in epigenetic regulation of gene transcription.", 
"Genetically identical cells grown in the same culture display striking cell-to-cell heterogeneity in gene expression and other traits. A crucial challenge is to understand how much of this heterogeneity reflects the noise tolerance of a robust system and how much serves a biological function. In bacteria, stochastic gene expression results in cell-to-cell heterogeneity that might serve as a bet-hedging mechanism, allowing a few cells to survive through an antimicrobial treatment while others perish. Despite its clinical importance, the molecular mechanisms underlying bet hedging remain unclear. Here, we investigate the mechanisms of bet hedging in Saccharomyces cerevisiae using a new high-throughput microscopy assay that monitors variable protein expression, morphology, growth rate, and survival outcomes of tens of thousands of yeast microcolonies simultaneously. We find that clonal populations display broad distributions of growth rates and that slow growth predicts resistance to heat killing in a probabalistic manner. We identify several gene products that are likely to play a role in bet hedging and confirm that Tsl1, a trehalose-synthesis regulator, is an important component of this resistance. Tsl1 abundance correlates with growth rate and replicative age and predicts survival. Our results suggest that yeast bet hedging results from multiple epigenetic growth states determined by a combination of stochastic and deterministic factors.", 
"Epigenetics, the transgenerational transfer of phenotypic characters without modification of gene sequence, is a burgeoning area of study in many disciplines of biology. However, the potential impact of this phenomenon on the physiology of animals is not yet broadly appreciated, in part because the phenomenon of epigenetics is not typically part of the design of physiological investigations. Still enigmatic and somewhat ill defined is the relationship between the overarching concept of epigenetics and interesting transgenerational phenomena (e.g. 'maternal/parental effects') that alter the physiological phenotype of subsequent generations. The lingering effect on subsequent generations of an initial environmental disturbance in parent animals can be profound, with genes continuing to be variously silenced or expressed without an associated change in gene sequence for many generations. Known epigenetic mechanisms involved in this phenomenon include chromatin remodeling (DNA methylation and histone modification), RNA-mediated modifications (non-coding RNA and microRNA), as well as other less well studied mechanisms such as self-sustaining loops and structural inheritance. In this review we: (1) discuss how the concepts of epigenetics and maternal effects both overlap with, and are distinct from, each other; (2) analyze examples of existing animal physiological studies based on these concepts; and (3) offer a construct by which to integrate these concepts into the design of future investigations in animal physiology.", 
"Bisphenol-A (BPA) is a nonsteroidal estrogen that is ubiquitous in the environment. The homeobox gene Hoxa10 controls uterine organogenesis, and its expression is affected by in utero BPA exposure. We hypothesized that an epigenetic mechanism underlies BPA-mediated alterations in Hoxa10 expression. We analyzed the expression pattern and methylation profile of Hoxa10 after in utero BPA exposure. Pregnant CD-1 mice were treated with BPA (5 mg/kg IP) or vehicle control on d 9-16 of pregnancy. Hoxa10 mRNA and protein expression were increased by 25% in the reproductive tract of mice exposed in utero. Bisulfite sequencing revealed that cytosine-guanine dinucleotide methylation was decreased from 67 to 14% in the promoter and from 71 to 3% in the intron of Hoxa10 after in utero BPA exposure. Decreased DNA methylation led to an increase in binding of ER-alpha to the Hoxa10 ERE both in vitro as and in vivo as determined by EMSA and chromatin immunoprecipitation, respectively. Diminished methylation of the ERE-containing promoter sequence resulted in an increase in ERE-driven gene expression in reporter assays. We identify altered methylation as a novel mechanism of BPA-induced altered developmental programming. Permanent epigenetic alteration of ERE sensitivity to estrogen may be a general mechanism through which endocrine disruptors exert their action.-Bromer, J. G., Zhou, Y., Taylor, M. B., Doherty, L., Taylor, H. S.. Bisphenol-A exposure in utero leads to epigenetic alterations in the developmental programming of uterine estrogen response. FASEB J. 24, 2273-2280 (2010). www.fasebj.org", 
"Background: Subtelomeres, regions proximal to telomeres, exhibit characteristics unique to eukaryotic genomes. Genes residing in these loci are subject to epigenetic regulation and elevated rates of both meiotic and mitotic recombination. However, most genome sequences do not contain assembled subtelomeric sequences, and, as a result, subtelomeres are often overlooked in comparative genomics. Results: We studied the evolution and functional divergence of subtelomeric gene families in the yeast lineage. Our computational results show that subtelomeric families are evolving and expanding much faster than families that do not contain subtelomeric genes. Focusing on three related subtelomeric MAL gene families involved in disaccharide metabolism that show typical patterns of rapid expansion and evolution, we show experimentally how frequent duplication events followed by functional divergence yield novel alleles that allow the metabolism of different carbohydrates. Conclusions: Taken together, our computational and experimental analyses show that the extraordinary instability of eukaryotic subtelomeres supports rapid adaptation to novel niches by promoting gene recombination and duplication followed by functional divergence of the alleles.", 
"DNA methylation is dynamically remodelled during the mammalian life cycle through distinct phases of reprogramming and de novo methylation. These events enable the acquisition of cellular potential followed by the maintenance of lineage-restricted cell identity, respectively, a process that defines the life cycle through successive generations. DNA methylation contributes to the epigenetic regulation of many key developmental processes including genomic imprinting, X-inactivation, genome stability and gene regulation. Emerging sequencing technologies have led to recent insights into the dynamic distribution of DNA methylation during development and the role of this epigenetic mark within distinct genomic contexts, such as at promoters, exons or imprinted control regions. Additionally, there is a better understanding of the mechanistic basis of DNA demethylation during epigenetic reprogramming in primordial germ cells and during pre-implantation development. Here, we discuss our current understanding of the developmental roles and dynamics of this key epigenetic system.", 
"MicroRNAs (miRNAs), small noncoding RNAs, can control gene expression by binding to their target genes for degradation and/or translational repression. Epigenetic mechanisms are defined as heritable changes in gene expression that do not involve coding sequence modifications. Both mechanisms play an important role in maintaining physiological functions and are also related to disease development. However, few studies report that miRNA-mediated epigenetic regulations are involved in atherosclerosis. In the present study, oxidized low-density lipoprotein (oxLDL) significantly increased primary human aortic smooth muscle cell (HASMC) migration through MMP-2/MMP-9 up-regulation associated with decreased DNA methylation levels. Either mRNA or protein level of DNA methyltransferase 3b (DNMT3b) showed a dose-dependent down-regulation in oxLDL-mediated HASMCs. Knockdown DNMT3b expression enhanced oxLDL-induced DNA demethylation levels of MMP-2/MMP-9. The expression of miRNA-29b (miR-29b), directly targeting DNMT3b, was up-regulated by oxLDL treatment in a dose-dependent manner. OxLDL-mediated MMP-2/MMP-9 up-regulation, DNMT3b down-regulation, and DNA demethylation were all attenuated after knockdown miR-29b expression by antagomiR-29b. We find that oxLDL can up-regulate miR-29b expression, resulting in DNMT3b down-regulation in HASMCs and epigenetically regulated MMP2/MMP-9 genes involved in cell migration. These results show that miRNA-mediated epigenetic regulation may be a novel mechanism in atherosclerosis.-Chen, K.-C., Wang, Y.-S., Hu, C.-Y., Chang, W.-C., Liao, Y C., Dai, C.-Y., Juo, S.-H. H. OxLDL up-regulates microRNA-29b, leading to epigenetic modifications of MMP-2/MMP-9 genes: a novel mechanism for cardiovascular diseases. FASEB J. 25, 1718-1728 (2011). www.fasebj.org", 
"Somatic cells have been reprogrammed into pluripotent stem cells by introducing a combination of several transcription factors, such as Oct3/4, Sox2, Klf4 and c-Myc. Induced pluripotent stem ( iPS) cells from a patient's somatic cells could be a useful source for drug discovery and cell transplantation therapies. However, most human iPS cells are made by viral vectors, such as retrovirus and lentivirus, which integrate the reprogramming factors into the host genomes and may increase the risk of tumour formation. Several non-integration methods have been reported to overcome the safety concern associated with the generation of iPS cells, such as transient expression of the reprogramming factors using adenovirus vectors or plasmids, and direct delivery of reprogramming proteins. Although these transient expression methods could avoid genomic alteration of iPS cells, they are inefficient. Several studies of gene expression, epigenetic modification and differentiation revealed the insufficient reprogramming of iPS cells, thus suggesting the need for improvement of the reprogramming procedure not only in quantity but also in quality. This report will summarize the current knowledge of iPS generation and discuss future reprogramming methods for medical application.", 
"Polycomb group (PcG) proteins form conserved regulatory complexes that modify chromatin to repress the genes that are not required in a specific differentiation status [1]. In animals, the two best-characterized PcG complexes are PRC2 and PRC1, which respectively possess histone 3 lysine 27 (H3K27) trimethyltransferase [2-4] and histone 2A lysine 119 (H2AK119) E3 ubiquitin ligase activities [5-7]. In Arabidopsis, PRC2 activity is also required for the gene silencing mechanism [8]; however, the existence of PRC1 has been questioned, because plant genomes do not encode clear PRC1 components and H2A monoubiquitination has not been detected [6, 9]. Conversely, recent reports have unveiled the presence of homologs to PRC1 components that together with plant-specific proteins could be part of the long-sought PRC1-like complexes [10, 11]. Here we show that the PRC1 RING-finger homologs AtBMI1A and AtBMI1B are implicated in the repression of embryonic and stem cell regulators. Plants impaired in AtBMI1A and AtBMI1B show derepression of embryonic traits in somatic cells, displaying a phenotype similar to plants mutant in PRC2 components [12-14]. Our data demonstrate that the AtBMI1A/B proteins mediate H2A monoubiquitination in Arabidopsis and that this mark, together with PRC2-mediated H3K27 trimethylation, plays a key role in maintaining cell identity.", 
"Histone modifications are thought to control the regulation of genetic programs in normal physiology and cancer. Methylation (mono-, di-, and tri-methylation) on histone H3 lysine (K) 27 induces transcriptional repression, and thereby participates in controlling gene expression patterns. Enhancer of zeste (EZH) 2, a methyltransferase and component of the polycomb repressive complex 2 (PRC2), plays an essential role in the epigenetic maintenance of the H3K27me3 repressive chromatin mark. Abnormal EZH2 expression has been associated with various cancers including breast cancer. Here, we discuss the contribution of EZH2 and the PRC2 complex in controlling the H3K27 methylation status and subsequent consequences on genomic instability and the cell cycle in breast cancer cells. We also discuss distinct molecular mechanisms used by EZH2 to suppress BRCA1 functions.", 
"Waddington's epigenetic landscape is probably the most famous and most powerful metaphor in developmental biology. Cells, represented by balls, roll downhill through a landscape of bifurcating valleys. Each new valley represents a possible cell fate and the ridges between the valleys maintain the cell fate once it has been chosen. Here I examine models of two important developmental processes - cell-fate induction and lateral inhibition - and ask whether the landscapes for these models at least qualitatively resemble Waddington's picture. For cell-fate induction, the answer is no. The commitment of a cell to a new fate corresponds to the disappearance of a valley from the landscape, not the splitting of one valley into two, and it occurs through a type of bifurcation - a saddle-node bifurcation - that possesses an intrinsic irreversibility that is missing from Waddington's picture. Lateral inhibition, a symmetrical cell-cell competition process, corresponds better to Waddington's picture, with one valley reversibly splitting into two through a pitchfork bifurcation. I propose an alternative epigenetic landscape that has numerous valleys and ridges right from the start, with the process of cell-fate commitment corresponding to the irreversible disappearance of some of these valleys and ridges, via cell-fate induction, complemented by the creation of new valleys and ridges through processes like cell-cell competition.", 
"During gametogenesis and pre-implantation development, the mammalian epigenome is reprogrammed to establish pluripotency in the epiblast. Here we show that the histone 3 lysine 4 (H3K4) methyltransferase, MLL2, controls most of the promoter-specific chromatin modification, H3K4me3, during oogenesis and early development. Using conditional knockout mutagenesis and a hypomorph model, we show that Mll2 deficiency in oocytes results in anovulation and oocyte death, with increased transcription of p53, apoptotic factors, and lap elements. MLL2 is required for (1) bulk H3K4me3 but not H3K4me1, indicating that MLL2 controls most promoters but monomethylation is regulated by a different H3K4 methyltransferase; (2) the global transcriptional silencing that preceeds resumption of meiosis but not for the concomitant nuclear reorganization into the surrounded nucleolus (SN) chromatin configuration; (3) oocyte survival; and (4) normal zygotic genome activation. These results reveal that MLL2 is autonomously required in oocytes for fertility and imply that MLL2 contributes to the epigenetic reprogramming that takes place before fertilization. We propose that once this task has been accomplished, MLL2 is not required until gastrulation and that other methyltransferases are responsible for bulk H3K4me3, thereby revealing an unexpected epigenetic control switch amongst the H3K4 methyltransferases during development.", 
"The consequences of early developmental conditions for performance in later life are now subjected to convergent interest from many different biological sub-disciplines. However, striking data, largely from the biomedical literature, show that environmental effects experienced even before conception can be transmissible to subsequent generations. Here, we review the growing evidence from natural systems for these cross-generational effects of early life conditions, showing that they can be generated by diverse environmental stressors, affect offspring in many ways and can be transmitted directly or indirectly by both parental lines for several generations. In doing so, we emphasize why early life might be so sensitive to the transmission of environmentally induced effects across generations. We also summarize recent theoretical advancements within the field of developmental plasticity, and discuss how parents might assemble different 'internal' and 'external' cues, even from the earliest stages of life, to instruct their investment decisions in offspring. In doing so, we provide a preliminary framework within the context of adaptive plasticity for understanding inter-generational phenomena that arise from early life conditions.", 
"Here, we describe that lysine-specific demethylase 1 (Lsd1/KDM1a), which demethylates histone H3 on Lys4 or Lys9 (H3K4/K9), is an indispensible epigenetic governor of hematopoietic differentiation. Integrative genomic analysis, combining global occupancy of Lsd1, genome-wide analysis of its substrates H3K4 monomethylation and dimethylation, and gene expression profiling, reveals that Lsd1 represses hematopoietic stem and progenitor cell (HSPC) gene expression programs during hematopoietic differentiation. We found that Lsd1 acts at transcription start sites, as well as enhancer regions. Loss of Lsd1 was associated with increased H3K4me1 and H3K4me2 methylation on HSPC genes and gene derepression. Failure to fully silence HSPC genes compromised differentiation of hematopoietic stem cells as well as mature blood cell lineages. Collectively, our data indicate that Lsd1-mediated concurrent repression of enhancer and promoter activity of stem and progenitor cell genes is a pivotal epigenetic mechanism required for proper hematopoietic maturation.", 
"Epigenetics could help to explain individual differences in weight loss after an energy-restriction intervention. Here, we identify novel potential epigenetic biomarkers of weight loss, comparing DNA methylation patterns of high and low responders to a hypocaloric diet. Twenty-five overweight or obese men participated in an 8-wk caloric restriction intervention. DNA was isolated from peripheral blood mononuclear cells and treated with bisulfite. The basal and endpoint epigenetic differences between high and low responders were analyzed by methylation microarray, which was also useful in comparing epigenetic changes due to the nutrition intervention. Subsequently, MALDI-TOF mass spectrometry was used to validate several relevant CpGs and the surrounding regions. DNA methylation levels in several CpGs located in the ATP10A and CD44 genes showed statistical baseline differences depending on the weight-loss outcome. At the treatment endpoint, DNA methylation levels of several CpGs on the WT1 promoter were statistically more methylated in the high than in the low responders. Finally, different CpG sites from WT1 and ATP10A were significantly modified as a result of the intervention. In summary, hypocaloric-diet-induced weight loss in humans could alter DNA methylation status of specific genes. Moreover, baseline DNA methylation patterns may be used as epigenetic markers that could help to predict weight loss.-Milagro, F. I., Campion, J., Cordero, P., Goyenechea, E., Gomez-Uriz, A. M., Abete, I., Zulet, M. A., Martinez, J. A. A dual epigenomic approach for the search of obesity biomarkers: DNA methylation in relation to diet-induced weight loss. FASEB J. 25, 1378-1389 (2011). www.fasebj.org", 
"Common themes are emerging in the molecular mechanisms of long non-coding RNA-mediated gene repression. Long non-coding RNAs (lncRNAs) participate in targeted gene silencing through chromatin remodelling, nuclear reorganisation, formation of a silencing domain and precise control over the entry of genes into silent compartments. The similarities suggest that these are fundamental processes of transcription regulation governed by lncRNAs. These findings have paved the way for analogous investigations on other lncRNAs and chromatin remodelling enzymes. Here we discuss these common mechanisms and provide our view on other molecules that warrant similar investigations. We also present our concepts on the possible mechanisms that may facilitate the exit of genes from the silencing domains and their potential therapeutic applications. Finally, we point to future areas of research and put forward our recommendations for improvements in resources and applications of existing technologies towards targeted outcomes in this active area of research.", 
"The epigenetic modification of chromatin structure and its effect on complex neuronal processes like learning and memory is an emerging field in neuroscience. However, little is known about the writers'' of the neuronal epigenome and how they lay down the basis for proper cognition. Here, we have dissected the neuronal function of the Drosophila euchromatin histone methyltransferase (EHMT), a member of a conserved protein family that methylates histone 3 at lysine 9 (H3K9). EHMT is widely expressed in the nervous system and other tissues, yet EHMT mutant flies are viable. Neurodevelopmental and behavioral analyses identified EHMT as a regulator of peripheral dendrite development, larval locomotor behavior, non-associative learning, and courtship memory. The requirement for EHMT in memory was mapped to 7B-Gal4 positive cells, which are, in adult brains, predominantly mushroom body neurons. Moreover, memory was restored by EHMT re-expression during adulthood, indicating that cognitive defects are reversible in EHMT mutants. To uncover the underlying molecular mechanisms, we generated genome-wide H3K9 dimethylation profiles by ChIP-seq. Loss of H3K9 dimethylation in EHMT mutants occurs at 5% of the euchromatic genome and is enriched at the 5' and 3' ends of distinct classes of genes that control neuronal and behavioral processes that are corrupted in EHMT mutants. Our study identifies Drosophila EHMT as a key regulator of cognition that orchestrates an epigenetic program featuring classic learning and memory genes. Our findings are relevant to the pathophysiological mechanisms underlying Kleefstra Syndrome, a severe form of intellectual disability caused by mutations in human EHMT1, and have potential therapeutic implications. Our work thus provides novel insights into the epigenetic control of cognition in health and disease.", 
"Acquired drug resistance is a major limitation for the successful treatment of cancer. Resistance can emerge due to a variety of reasons including host environmental factors as well as genetic or epigenetic alterations in the cancer cells. Evolutionary theory has contributed to the understanding of the dynamics of resistance mutations in a cancer cell population, the risk of resistance pre-existing before the initiation of therapy, the composition of drug cocktails necessary to prevent the emergence of resistance, and optimum drug administration schedules for patient populations at risk of evolving acquired resistance. Here we review recent advances towards elucidating the evolutionary dynamics of acquired drug resistance and outline how evolutionary thinking can contribute to outstanding questions in the field. Published by Elsevier Ltd.", 
"DNA methylation is an epigenetic modification associated with gene silencing. In Arabidopsis, DNA methylation is established by DOMAINS REARRANGED METHYLTRANSFERASE 2 (DRM2), which is targeted by small interfering RNAs through a pathway termed RNA-directed DNA methylation (RdDM) [1, 2]. Recently, RdDM was shown to require intergenic noncoding (IGN) transcripts that are dependent on the Pol V polymerase. These transcripts are proposed to function as scaffolds for the recruitment of downstream RdDM proteins, including DRM2, to loci that produce both siRNAs and IGN transcripts [3]. However, the mechanism(s) through which Pol V is targeted to specific genomic loci remains largely unknown. Through affinity purification of two known RdDM components, DEFECTIVE IN RNA-DIRECTED DNA METHYLATION 1 (DRD1) [4] and DEFECTIVE IN MERISTEM SILENCING 3 (DMS3) [5, 6], we found that they copurify with each other and with a novel protein, RNA-DIRECTED DNA METHYLATION 1 (RDM1), forming a complex we term DDR. We also found that DRD1 copurified with Pol V subunits and that RDM1, like DRD1 [3] and DMS3 [7], is required for the production of Pol V-dependent transcripts. These results suggest that the DDR complex acts in RdDM at a step upstream of the recruitment or activation of Pol V.", 
"The Neo-Darwinian concept of natural selection is plausible when one assumes a straightforward causation of phenotype by genotype. However, such simple 1:1 mapping must now give place to the modern concepts of gene regulatory networks and gene expression noise. Both can, in the absence of genetic mutations, jointly generate a diversity of inheritable randomly occupied phenotypic states that could also serve as a substrate for natural selection. This form of epigenetic dynamics challenges Neo-Darwinism. It needs to incorporate the non-linear, stochastic dynamics of gene networks. A first step is to consider the mathematical correspondence between gene regulatory networks and Waddington's metaphoric epigenetic landscape, which actually represents the quasi-potential function of global network dynamics. It explains the coexistence of multiple stable phenotypes within one genotype. The landscape's topography with its attractors is shaped by evolution through mutational re-wiring of regulatory interactions offering a link between genetic mutation and sudden, broad evolutionary changes.", 
"Over two decades of research have demonstrated that the peptide hormone endothelin-1 (ET-1) plays multiple, complex roles in cardiovascular, neural, pulmonary, reproductive, and renal physiology. Differential and tissue-specific production of ET-1 must be tightly regulated in order to preserve these biologically diverse actions. The primary mechanism thought to control ET-1 bioavailability is the rate of transcription from the ET-1 gene (edn1). Studies conducted on a variety of cell types have identified key transcription factors that govern edn1 expression. With few exceptions, the cis-acting elements bound by these factors have been mapped in the edn1 regulatory region. Recent evidence has revealed new roles for some factors originally believed to regulate edn1 in a tissue or hormone-specific manner. In addition, other mechanisms involved in epigenetic regulation and mRNA stability have emerged as important processes for regulated edn1 expression. The goal of this review is to provide a comprehensive overview of the specific factors and signaling systems that govern edn1 activity at the molecular level.-Stow, L. R., Jacobs, M. E., Wingo, C. S., Cain, B. D. Endothelin-1 gene regulation. FASEB J. 25, 16-28 (2011). www.fasebj.org", 
"In most eukaryotes, the HISTONE 3 family comprises several variants distinguished by their amino acid sequence, localization, and correlation with transcriptional activity [1-3]. Transgenerational inheritance of epigenetic information carried by histones is still unclear [4, 5]. In addition to covalent histone modifications, the mosaic distribution of H3 variants onto chromatin has been proposed to provide a new level of epigenetic information [6]. To study the transmission of patterns of H3 variants through generations, we combined transcriptional profiling and live imaging of the 13 H3 variants encoded by the Arabidopsis plant genome [7]. In comparison with somatic cells, only a restricted number of H3 variants are present in male and female gametes. Upon fertilization, H3 variants contributed by both gametes are actively removed from the zygote chromatin. The somatic H3 composition is restored in the embryo by de novo synthesis of H3 variants. A survey of Arabidopsis homologs of animal H3 chaperones suggests that removal of parental H3 from the zygote nucleus relies on a new mechanism. Our results suggest that reprogramming of parental genomes in the zygote limits the inheritance of epigenetic information carried by H3 variants across generations.", 
"Fundamental to genomic imprinting in mammals is the acquisition of epigenetic marks that differ in male and female gametes at 'imprinting control regions' (ICRs). These marks mediate the allelic expression of imprinted genes in the offspring. Much has been learnt about the nature of imprint marks, the times during gametogenesis at which they are laid down and some of the factors responsible especially for DNA methylation. Recent work has revealed that transcription and histone modifications are critically involved in DNA methylation acquisition, and these findings allow us to propose rational models for methylation establishment. A completely novel perspective on gametic DNA methylation has emerged from epigenomic profiling. Far more differentially methylated loci have been identified in gametes than known imprinted genes, which leads us to revise the notion that methylation of ICRs is a specifically targeted process. Instead, it seems to obey default processes in germ cells, giving rise to distinct patterns of DNA methylation in sperm and oocytes. This new insight, together with the identification of proteins that preserve DNA methylation after fertilization, emphasizes the key role played by mechanisms that selectively retain differential methylation at imprinted loci during early development. Addressing these mechanisms will be essential to understanding the specificity and evolution of genomic imprinting.", 
"DNA methylation maintains genome stability and regulates gene expression [1]. In mammals, DNA methylation is reprogrammed in the germline from one generation to the next [2]. In plants, it was considered that patterns of DNA methylation are stably maintained through sexual reproduction [3-6]. However, a recent report showed discrete variations of DNA methylation profiles from mother to daughter plants [7]. The mechanisms that explain these variations have remained unknown. Here, we report that maintenance DNA methyltransferases are barely expressed during Arabidopsis female gametogenesis. In contrast, after fertilization both maintenance and de novo DNA methyltransferases are expressed strongly in the embryo. Embryogenesis is marked by increased de novo DNA methylation, reaching levels that are further maintained in the adult plant. The accumulation of these epigenetic marks after fertilization silences a methylation-sensitive fluorescent reporter. De novo DNA methylation in the embryo provides a mechanism that could account for the gradual remethylation of experimentally demethylated genomes [8, 9]. In conclusion, we uncover that DNA methylation activity fluctuates during sexual reproduction. This cycle likely explains variations of genome-wide patterns of DNA methylation across generations in Arabidopsis [7, 10] and enables a limited degree of reprogramming of the epigenome.", 
"We hypothesize that heritable epigenetic changes can affect rates of fitness increase as well as patterns of genotypic and phenotypic change during adaptation. In particular, we suggest that when natural selection acts on pure epigenetic variation in addition to genetic variation, populations adapt faster, and adaptive phenotypes can arise before any genetic changes. This may make it difficult to reconcile the timing of adaptive events detected using conventional population genetics tools based on DNA sequence data with environmental drivers of adaptation, such as changes in climate. Epigenetic modifications are frequently associated with somatic cell differentiation, but recently epigenetic changes have been found that can be transmitted over many generations. Here, we show how the interplay of these heritable epigenetic changes with genetic changes can affect adaptive evolution, and how epigenetic changes affect the signature of selection in the genetic record.", 
"The in utero availability of methyl donors, such as choline, may modify fetal epigenetic marks and lead to sustainable functional alterations throughout the life course. The hypothalamic-pituitary-adrenal (HPA) axis regulates cortisol production and is sensitive to perinatal epigenetic programming. As an extension of a 12-wk dose-response choline feeding study conducted in third-trimester pregnant women, we investigated the effect of maternal choline intake (930 vs. 480 mg/d) on the epigenetic state of cortisol-regulating genes, and their expression, in placenta and cord venous blood. The higher maternal choline intake yielded higher placental promoter methylation of the cortisol-regulating genes, corticotropin releasing hormone (CRH; P = 0.05) and glucocorticoid receptor (NR3C1; P = 0.002); lower placental CRH transcript abundance (P = 0.04); lower cord blood leukocyte promoter methylation of CRH (P = 0.05) and NR3C1 (P = 0.04); and 33% lower (P = 0.07) cord plasma cortisol. In addition, placental global DNA methylation and dimethylated histone H3 at lysine 9 (H3K9me2) were higher (P = 0.02) in the 930 mg choline/d group, as was the expression of select placental methyltransferases. These data collectively suggest that maternal choline intake in humans modulates the epigenetic state of genes that regulate fetal HPA axis reactivity as well as the epigenomic status of fetal derived tissues.-Jiang, X., Yan, J., West, A. A., Perry, C. A., Malysheva, O. V., Devapatla, S., Pressman, E., Vermeylen, F., Caudill, M. A. Maternal choline intake alters the epigenetic state of fetal cortisol-regulating genes in humans. FASEB J. 26, 3563-3574 (2012). www.fasebj.org", 
"Even though schizophrenia has a strong hereditary component, departures from simple genetic transmission are prominent. DNA methylation has emerged as an epigenetic explanatory candidate of schizophrenia's nonmendelian characteristics. To investigate this assumption, we examined genome-wide (global) and gene-specific DNA methylation levels, which are associated with genomic stability and gene expression activity, respectively. Analyses were conducted using DNA from leukocytes of patients with schizophrenia and controls. Global methylation results revealed a highly significant hypomethylation in patients with schizophrenia (P<2.0 x 10(-6)) and linear regression among patients generated a model in which antipsychotic treatment and disease onset explained 11% of the global methylation variance (adjusted R-2=0.11, ANOVA P<0.001). Specifically, haloperidol was associated with higher (control-like) methylation (P=0.001), and early onset (a putative marker of schizophrenia severity) was associated with lower methylation (P=0.002). With regard to the gene-specific methylation analyses, and in accordance with the dopamine hypothesis of psychosis, we found that the analyzed region of S-COMT was hypermethylated in patients with schizophrenia (P=0.004). In summary, these data support the notion of a dysregulated epigenome in schizophrenia, which, at least globally, is more pronounced in early-onset patients and can be partly rescued by antipsychotic medication. In addition, blood DNA-methylation signatures show promise of serving as a schizophrenia biomarker in the future.-Melas, P. A., Rogdaki, M., sby, U., Schalling, M., Lavebratt, C., Ekstrom, T. J. Epigenetic aberrations in leukocytes of patients with schizophrenia: association of global DNA methylation with antipsychotic drug treatment and disease onset. FASEB J. 26, 2712-2718 (2012). www.fasebj.org", 
"The centromere, responsible for chromosome segregation during mitosis, is epigenetically defined by CENP-A containing chromatin. The amount of centromeric CENP-A has direct implications for both the architecture and epigenetic inheritance of centromeres. Using complementary strategies, we determined that typical human centromeres contain similar to 400 molecules of CENP-A, which is controlled by a mass-action mechanism. This number, despite representing only similar to 4% of all centromeric nucleosomes, forms a similar to 50-fold enrichment to the overall genome. In addition, although pre-assembled CENP-A is randomly segregated during cell division, this amount of CENP-A is sufficient to prevent stochastic loss of centromere function and identity. Finally, we produced a statistical map of CENP-A occupancy at a human neocentromere and identified nucleosome positions that feature CENP-A in a majority of cells. In summary, we present a quantitative view of the centromere that provides a mechanistic framework for both robust epigenetic inheritance of centromeres and the paucity of neocentromere formation.", 
"Long non-coding RNAs (lncRNAs), which represent a new frontier in molecular biology, play important roles in regulating gene expression at epigenetic, transcriptional and post-transcriptional levels. More and more lncRNAs have been found to play important roles in normal cell physiological activities, and participate in the development of varieties of tumors and other diseases. Previously, we have only been able to determine the function of lncRNAs through multiple mechanisms, including genetic imprinting, chromatin remodeling, splicing regulation, mRNA decay, and translational regulation. Application of technological advances to research into the function of lncRNAs is extremely important. The major tools for exploring lncRNAs include microarrays, RNA sequencing (RNA-seq), Northern blotting, real-time quantitative reverse transcription-polymerase chain reaction (qRT-PCR), fluorescence in situ hybridization (FISH), RNA interference (RNAi), RNA-binding protein immunoprecipitation (RIP), chromatin isolation by RNA purification (ChIRP), crosslinking-immunopurification (CLIP), and bioinformatic prediction. In this review, we highlight the functions of lncRNAs, and advanced methods to research lncRNA-protein interactions.", 
"To explore the potential evolutionary relevance of heritable epigenetic variation, the National Evolutionary Synthesis Center recently hosted a catalysis meeting that brought together molecular epigeneticists, experimental evolutionary ecologists, and theoretical population and quantitative geneticists working across a wide variety of systems. The group discussed the methods available to investigate epigenetic variation and epigenetic inheritance, and how to evaluate their importance for phenotypic evolution. We found that understanding tire relevance of epigenetic effects in phenotypic evolution will require clearly delineating epigenetics within existing terminology and expanding research efforts into ecologically relevant circumstances across model and nonmodel organisms. In addition, a critical component of understanding epigenetics will be the development of new and current statistical approaches and expansion of quantitative and population genetic theory Although the importance of heritable epigenetic effects on evolution is still under discussion, investigating them in the context of a multidisciplinary approach could transform the field.", 
"Two-thirds of gene promoters in mammals are associated with regions of non-methylated DNA, called CpG islands (CGIs), which counteract the repressive effects of DNA methylation on chromatin. In cold-blooded vertebrates, computational CGI predictions often reside away from gene promoters, suggesting a major divergence in gene promoter architecture across vertebrates. By experimentally identifying non-methylated DNA in the genomes of seven diverse vertebrates, we instead reveal that non-methylated islands (NMIs) of DNA are a central feature of vertebrate gene promoters. Furthermore, NMIs are present at orthologous genes across vast evolutionary distances, revealing a surprising level of conservation in this epigenetic feature. By profiling NMIs in different tissues and developmental stages we uncover a unifying set of features that are central to the function of NMIs in vertebrates. Together these findings demonstrate an ancient logic for NMI usage at gene promoters and reveal an unprecedented level of epigenetic conservation across vertebrate evolution.", 
"The PRDM family has recently spawned considerable interest as it has been implicated in fundamental aspects of cellular differentiation and exhibits expanding ties to human diseases. The PRDMs belong to the SET domain family of histone methyltransferases, however, enzymatic activity has been determined for only few PRDMs suggesting that they act by recruiting co-factors or, more speculatively, confer methylation of non-histone targets. Several PRDM family members are deregulated in human diseases, most prominently in hematological malignancies and solid cancers, where they can act as both tumor suppressors or drivers of oncogenic processes. The molecular mechanisms have been delineated for only few PRDMs and little is known about functional redundancy within the family. Future studies should identify target genes of PRDM proteins and the protein complexes in which PRDM proteins reside to provide a more comprehensive understanding of the biological and biochemical functions of this important protein family.", 
"Interactions of cell-autonomous circadian oscillators with diurnal cycles govern the temporal compartmentalization of cell physiology in mammals. To understand the transcriptional and epigenetic basis of diurnal rhythms in mouse liver genome-wide, we generated temporal DNA occupancy profiles by RNA polymerase II (Pol II) as well as profiles of the histone modifications H3K4me3 and H3K36me3. We used these data to quantify the relationships of phases and amplitudes between different marks. We found that rhythmic Pol II recruitment at promoters rather than rhythmic transition from paused to productive elongation underlies diurnal gene transcription, a conclusion further supported by modeling. Moreover, Pol II occupancy preceded mRNA accumulation by 3 hours, consistent with mRNA half-lives. Both methylation marks showed that the epigenetic landscape is highly dynamic and globally remodeled during the 24-hour cycle. While promoters of transcribed genes had tri-methylated H3K4 even at their trough activity times, tri-methylation levels reached their peak, on average, 1 hour after Pol II. Meanwhile, rhythms in tri-methylation of H3K36 lagged transcription by 3 hours. Finally, modeling profiles of Pol II occupancy and mRNA accumulation identified three classes of genes: one showing rhythmicity both in transcriptional and mRNA accumulation, a second class with rhythmic transcription but flat mRNA levels, and a third with constant transcription but rhythmic mRNAs. The latter class emphasizes widespread temporally gated posttranscriptional regulation in the mouse liver.", 
"Telomeres protect the chromosome ends from unscheduled DNA repair and degradation. Telomeres are heterochromatic domains composed of repetitive DNA (TTAGGG repeats) bound to an array of specialized proteins. The length of telomere repeats and the integrity of telomere-binding proteins are both important for telomere protection. Furthermore, telomere length and integrity are regulated by a number of epigenetic modifications, thus pointing to higher order control of telomere function. In this regard, we have recently discovered that telomeres are transcribed generating long, non-coding RNAs, which remain associated with the telomeric chromatin and are likely to have important roles in telomere regulation. In the past, we showed that telomere length and the catalytic component of telomerase, Tert, are critical determinants for the mobilization of stem cells. These effects of telomerase and telomere length on stem cell behaviour anticipate the premature ageing and cancer phenotypes of telomerase mutant mice. Recently, we have demonstrated the anti-ageing activity of telomerase by forcing telomerase expression in mice with augmented cancer resistance. Shelterin is the major protein complex bound to mammalian telomeres; however, its potential relevance for cancer and ageing remained unaddressed to date. To this end, we have generated mice conditionally deleted for the shelterin proteins TRF1, TPP1 and Rap1. The study of these mice demonstrates that telomere dysfunction, even if telomeres are of a normal length, is sufficient to produce premature tissue degeneration, acquisition of chromosomal aberrations and initiation of neoplastic lesions. These new mouse models, together with the telomerase-deficient mouse model, are valuable tools for understanding human pathologies produced by telomere dysfunction.", 
"The basic unit of genome packaging is the nucleosome, and nucleosomes have long been proposed to restrict DNA accessibility both to damage and to transcription. Nucleosome number in cells was considered fixed, but recently aging yeast and mammalian cells were shown to contain fewer nucleosomes. We show here that mammalian cells lacking High Mobility Group Box 1 protein (HMGB1) contain a reduced amount of core, linker, and variant histones, and a correspondingly reduced number of nucleosomes, possibly because HMGB1 facilitates nucleosome assembly. Yeast nhp6 mutants lacking Nhp6a and -b proteins, which are related to HMGB1, also have a reduced amount of histones and fewer nucleosomes. Nucleosome limitation in both mammalian and yeast cells increases the sensitivity of DNA to damage, increases transcription globally, and affects the relative expression of about 10% of genes. In yeast nhp6 cells the loss of more than one nucleosome in four does not affect the location of nucleosomes and their spacing, but nucleosomal occupancy. The decrease in nucleosomal occupancy is non-uniform and can be modelled assuming that different nucleosomal sites compete for available histones. Sites with a high propensity to occupation are almost always packaged into nucleosomes both in wild type and nucleosome-depleted cells; nucleosomes on sites with low propensity to occupation are disproportionately lost in nucleosome-depleted cells. We suggest that variation in nucleosome number, by affecting nucleosomal occupancy both genomewide and gene-specifically, constitutes a novel layer of epigenetic regulation.", 
"The multifunctional zinc-finger protein CCCTC-binding factor (CTCF) is a very strong candidate for the role of coordinating the expression level of coding sequences with their three-dimensional position in the nucleus, apparently responding to a code in the DNA itself. Dynamic interactions between chromatin fibers in the context of nuclear architecture have been implicated in various aspects of genome functions. However, the molecular basis of these interactions still remains elusive and is a subject of intense debate. Here we discuss the nature of CTCF-DNA interactions, the CTCF-binding specificity to its binding sites and the relationship between CTCF and chromatin, and we examine data linking CTCF with gene regulation in the three-dimensional nuclear space. We discuss why these features render CTCF a very strong candidate for the role and propose a unifying model, the CTCF code, explaining the mechanistic basis of how the information encrypted in DNA may be interpreted by CTCF into diverse nuclear functions.", 
"Somatic cell nuclear transfer (SCNT) cloning is the sole reproductive engineering technology that endows the somatic cell genome with totipotency. Since the first report on the birth of a cloned sheep from adult somatic cells in 1997, many technical improvements in SCNT have been made by using different epigenetic approaches, including enhancement of the levels of histone acetylation in the chromatin of the reconstructed embryos. Although it will take a considerable time before we fully understand the nature of genomic programming and totipotency, we may expect that somatic cell cloning technology will soon become broadly applicable to practical purposes, including medicine, pharmaceutical manufacturing and agriculture. Here we review recent progress in somatic cell cloning, with a special emphasis on epigenetic studies using the laboratory mouse as a model.", 
"Long non-coding RNAs (lncRNAs) are transcripts with low protein-coding potential that represent a large proportion of the transcriptional output of the cell. Many lncRNAs exhibit features indicative of functionality including tissue-restricted expression, localization to distinct subcellular structures, regulated expression and evolutionary conservation. Some lncRNAs have been shown to associate with chromatin-modifying activities and transcription factors, suggesting that a common mode of action may be to guide protein complexes to target genomic loci. However, the functions (if any) of the vast majority of lncRNA transcripts are currently unknown, and the subject of investigation. Here, we consider the putative role(s) of lncRNAs in neurodevelopment and brain function with an emphasis on the epigenetic regulation of gene expression. Associations of lncRNAs with neurodevelopmental/neuropsychiatric disorders, neurodegeneration and brain cancers are also discussed.", 
"Compelling evidence suggests that the transcription factor Foxp3 acts as a master switch governing the development and function of CD4(+) regulatory T cells (Tregs). However, whether transcriptional control of Foxp3 expression itself contributes to the development of a stable Treg lineage has thus far not been investigated. We here identified an evolutionarily conserved region within the foxp3 locus upstream of exon-1 possessing transcriptional activity. Bisulphite sequencing and chromatin immunoprecipitation revealed complete demethylation of CpG motifs as well as histone modifications within the conserved region in ex vivo isolated Foxp3(+)CD25(+)CD4(+) Tregs, but not in naive CD25(-) CD4(+) T cells. Partial DNA demethylation is already found within developing Foxp3(+) thymocytes; however, Tregs induced by TGF-beta in vitro display only incomplete demethylation despite high Foxp3 expression. In contrast to natural Tregs, these TGF-beta-induced Foxp3(+) Tregs lose both Foxp3 expression and suppressive activity upon restimulation in the absence of TGF-beta. Our data suggest that expression of Foxp3 must be stabilized by epigenetic modification to allow the development of a permanent suppressor cell lineage, a finding of significant importance for therapeutic applications involving induction or transfer of Tregs and for the understanding of long-term cell lineage decisions.", 
"This review describes new developments in the study of transgenerational epigenetic inheritance, a component of epigenetics. We start by examining the basic concepts of the field and the mechanisms that underlie epigenetic inheritance. We present a comprehensive review of transgenerational cellular epigenetic inheritance among different taxa in the form of a table, and discuss the data contained therein. The analysis of these data shows that epigenetic inheritance is ubiquitous and suggests lines of research that go beyond present approaches to the subject. We conclude by exploring some of the consequences of epigenetic inheritance for the study of evolution, while also pointing to the importance of recognizing and understanding epigenetic inheritance for practical and theoretical issues in biology.", 
"Induced pluripotent stem (iPS) cells are generated from somatic cells by genetic manipulation. Reprogramming entails multiple transgene integrations and occurs apparently stochastically in rare cells over many days. Tissue stem cells may be subject to less-stringent epigenetic restrictions than other cells and might therefore be more amenable to deprogramming. We report that brain-derived neural stem (NS) cells acquire undifferentiated morphology rapidly and at high frequency after a single round of transduction with reprogramming factors. However, critical attributes of true pluripotency-including stable expression of endogenous Oct4 and Nanog, epigenetic erasure of X chromosome silencing in female cells, and ability to colonise chimaeras-were not attained. We therefore applied molecularly defined conditions for the derivation and propagation of authentic pluripotent stem cells from embryos. We combined dual inhibition (2i) of mitogen-activated protein kinase signalling and glycogen synthase kinase-3 (GSK3) with the self-renewal cytokine leukaemia inhibitory factor (LIF). The 2i/LIF condition induced stable up-regulation of Oct4 and Nanog, reactivation of the X chromosome, transgene silencing, and competence for somatic and germline chimaerism. Using 2i/LIF, NS cell reprogramming required only 1-2 integrations of each transgene. Furthermore, transduction with Sox2 and c-Myc is dispensable, and Oct4 and Klf4 are sufficient to convert NS cells into chimaera-forming iPS cells. These findings demonstrate that somatic cell state influences requirements for reprogramming and delineate two phases in the process. The ability to capture pre-pluripotent cells that can advance to ground state pluripotency simply and with high efficiency opens a door to molecular dissection of this remarkable phenomenon.", 
"Biomedical science has little considered the relevance of life history theory and evolutionary and ecological developmental biology to clinical medicine. However, the observations that early life influences can alter later disease risk-the developmental origins of health and disease (DOHaD) paradigm-have led to a recognition that these perspectives can inform our understanding of human biology. We propose that the DOHaD phenomenon can be considered as a subset of the broader processes of developmental plasticity by which organisms adapt to their environment during their life course. Such adaptive processes allow genotypic variation to be preserved through transient environmental changes. Cues for plasticity operate particularly during early development; they may affect a single organ or system, but generally they induce integrated adjustments in the mature phenotype, a process underpinned by epigenetic mechanisms and influenced by prediction of the mature environment. In mammals, an adverse intrauterine environment results in an integrated suite of responses, suggesting the involvement of a few key regulatory genes, that resets the developmental trajectory in expectation of poor postnatal conditions. Mismatch between the anticipated and the actual mature environment exposes the organism to risk of adverse consequences-the greater the mismatch, the greater the risk. For humans, prediction is inaccurate for many individuals because of changes in the postnatal environment toward energy-dense nutrition and low energy expenditure, contributing to the epidemic of chronic noncommunicable disease. This view of human disease from the perspectives of life history biology and evolutionary theory offers new approaches to prevention, diagnosis and intervention.", 
"Age-related defects in stem cells can limit proper tissue maintenance and hence contribute to a shortened lifespan. Using highly purified hematopoietic stem cells from mice aged 2 to 21 mo, we demonstrate a deficit in function yet an increase in stem cell number with advancing age. Expression analysis of more than 14,000 genes identified 1,500 that were age-induced and 1,600 that were age-repressed. Genes associated with the stress response, inflammation, and protein aggregation dominated the up-regulated expression profile, while the down-regulated profile was marked by genes involved in the preservation of genomic integrity and chromatin remodeling. Many chromosomal regions showed coordinate loss of transcriptional regulation; an overall increase in transcriptional activity with age and inappropriate expression of genes normally regulated by epigenetic mechanisms was also observed. Hematopoietic stem cells from early-aging mice expressing a mutant p53 allele reveal that aging of stem cells can be uncoupled from aging at an organismal level. These studies show that hematopoietic stem cells are not protected from aging. Instead, loss of epigenetic regulation at the chromatin level may drive both functional attenuation of cells, as well as other manifestations of aging, including the increased propensity for neoplastic transformation.", 
"Trimethylation of histone H3 lysine 27 (H3K27me3) plays critical roles in regulating animal development, and in several cases, H3K27me3 is also required for the proper expression of developmentally important genes in plants. However, the extent to which H3K27me3 regulates plant genes on a genome-wide scale remains unknown. In addition, it is not clear whether the establishment and spreading of H3K27me3 occur through the same mechanisms in plants and animals. We identified regions containing H3K27me3 in the genome of the flowering plant Arabidopsis thaliana using a high-density whole-genome tiling microarray. The results suggest that H3K27me3 is a major silencing mechanism in plants that regulates an unexpectedly large number of genes in Arabidopsis (similar to 4,400), and that the maintenance of H3K27me3 is largely independent of other epigenetic pathways, such as DNA methylation or RNA interference. Unlike in animals, where H3K27m3 occupies large genomic regions, in Arabidopsis, we found that H3K27m3 domains were largely restricted to the transcribed regions of single genes. Furthermore, unlike in animals systems, H3K27m3 domains were not preferentially associated with low-nucleosome density regions. The results suggest that different mechanisms may underlie the establishment and spreading of H3K27me3 in plants and animals.", 
"The relative contribution of genetic and environmental influences to the US black-white disparity in cardiovascular disease (CVD) is hotly debated within the public health, anthropology, and medical communities. In this article, we review evidence for developmental and epigenetic pathways linking early life environments with CVD, and critically evaluate their possible role in the origins of these racial health disparities. African Americans not only suffer from a disproportionate burden of CVD relative to whites, but also have higher rates of the perinatal health disparities now known to be the antecedents of these conditions. There is extensive evidence for a social origin to prematurity and low birth weight in African Americans, reflecting pathways such as the effects of discrimination on maternal stress physiology. In light of the inverse relationship between birth weight and adult CVD, there is now a strong rationale to consider developmental and epigenetic mechanisms as links between early life environmental factors like maternal stress during pregnancy and adult race-based health disparities in diseases like hypertension, diabetes, stroke, and coronary heart disease. The model outlined here builds upon social constructivist perspectives to highlight an important set of mechanisms by which social influences can become embodied, having durable and even transgenerational influences on the most pressing US health disparities. We conclude that environmentally responsive phenotypic plasticity, in combination with the better-studied acute and chronic effects of social-environmental exposures, provides a more parsimonious explanation than genetics for the persistence of CVD disparities between members of socially imposed racial categories. Am. J. Hum. Biol. 21:2-15, 2009. (C) 2008 Wiley-Liss, Inc.", 
"Cytosine methylation of repetitive sequences is widespread in plant genomes, occurring in both symmetric (CpG and CpNpG) as well as asymmetric sequence contexts. We used the methylation- dependent restriction enzyme McrBC to profile methylated DNA using tiling microarrays of Arabidopsis Chromosome 4 in two distinct ecotypes, Columbia and Landsberg erecta. We also used comparative genome hybridization to profile copy number polymorphisms. Repeated sequences and transposable elements (TEs), especially long terminal repeat retrotransposons, are densely methylated, but one third of genes also have low but detectable methylation in their transcribed regions. While TEs are almost always methylated, genic methylation is highly polymorphic, with half of all methylated genes being methylated in only one of the two ecotypes. A survey of loci in 96 Arabidopsis accessions revealed a similar degree of methylation polymorphism. Within-gene methylation is heritable, but is lost at a high frequency in segregating F-2 families. Promoter methylation is rare, and gene expression is not generally affected by differences in DNA methylation. Small interfering RNA are preferentially associated with methylated TEs, but not with methylated genes, indicating that most genic methylation is not guided by small interfering RNA. This may account for the instability of gene methylation, if occasional failure of maintenance methylation cannot be restored by other means.", 
"Polyploidy is produced by multiplication of a single genome (autopolyploid) or combination of two or more divergent genomes (allopolyploid). The available data obtained from the study of synthetic (newly created or human-made) plant allopolyploids have documented dynamic and stochastic changes in genomic organization and gene expression, including sequence elimination, inter-chromosomal exchanges, cytosine methylation, gene repression, novel activation, genetic dominance, subfunctionalization and transposon activation. The underlying mechanisms for these alterations are poorly understood. To promote a better understanding of genomic and gene expression changes in polyploidy, we briefly review origins and forms of polyploidy and summarize what has been learned from genome-wide gene expression analyses in newly synthesized auto- and allopolyploids. We show transcriptome divergence between the progenitors and in the newly formed allopolyploids. We propose models for transcriptional regulation, chromatin modification and RNA-mediated pathways in establishing locus-specific expression of orthologous and homoeologous genes during allopolyploid formation and evolution.", 
"In mammals, the X and Y chromosomes are subject to meiotic sex chromosome inactivation (MSCI) during prophase I in the male germline, but their status thereafter is currently unclear. An abundance of X-linked spermatogenesis genes has spawned the view that the X must be active [1-8]. On the other hand, the idea that the imprinted paternal X of the early embryo may be preinactivated by MSCI suggests that silencing may persist longer [9-12]. To clarify this issue, we establish a comprehensive X-expression profile during mouse spermatogenesis. Here, we discover that the X and Y occupy a novel compartment in the postmeiotic spermatid and adopt a non-Rabl configuration. We demonstrate that this postmeiotic sex chromatin (PMSC) persists throughout spermiogenesis into mature sperm and exhibits epigenetic similarity to the XY body. In the spermatid, 87% of X-linked genes remain suppressed postmeiotically, while autosomes are largely active. We conclude that chromosome-wide X silencing continues from meiosis to the end of spermiogenesis, and we discuss implications for proposed mechanisms of imprinted X-inactivation.", 
"Many genes are recruited to the nuclear periphery upon transcriptional activation. The mechanism and functional significance of this recruitment is unclear. We find that recruitment of the yeast INO1 and GAL1 genes to the nuclear periphery is rapid and independent of transcription. Surprisingly, these genes remain at the periphery for generations after they are repressed. Localization at the nuclear periphery serves as a form of memory of recent transcriptional activation, promoting reactivation. Previously expressed GAL1 at the nuclear periphery is activated much more rapidly than long- term repressed GAL1 in the nucleoplasm, even after six generations of repression. Localization of INO1 at the nuclear periphery is necessary and sufficient to promote more rapid activation. This form of transcriptional memory is chromatin based; the histone variant H2A. Z is incorporated into nucleosomes within the recently repressed INO1 promoter and is specifically required for rapid reactivation of both INO1 and GAL1. Furthermore, H2A. Z is required to retain INO1 at the nuclear periphery after repression. Therefore, H2A. Z-mediated localization of recently repressed genes at the nuclear periphery represents an epigenetic state that confers memory of transcriptional activation and promotes reactivation.", 
"There is increasing evidence that dynamic changes to chromatin, chromosomes and nuclear architecture are regulated by RNA signalling. Although the precise molecular mechanisms are not well understood, they appear to involve the differential recruitment of a hierarchy of generic chromatin modifying complexes and DNA methyltransferases to specific loci by RNAs during differentiation and development. A significant fraction of the genome-wide transcription of non-protein coding RNAs may be involved in this process, comprising a previously hidden layer of intermediary genetic information that underpins developmental ontogeny and the differences between species, ecotypes and individuals. It is also evident that RNA editing is a primary means by which hardwired genetic information in animals can be altered by environmental signals, especially in the brain, indicating a dynamic RNA-mediated interplay between the transcriptome, the environment and the epigenome. Moreover, RNA-directed regulatory processes may also transfer epigenetic information not only within cells but also between cells and organ systems, as well as across generations.", 
"Epigenetic gene silencing suppresses transposon activity and is critical for normal development [1, 2]. Two common epigenetic gene-silencing marks are DNA methylation and histone H3 lysine 9 dimethylation (H3K9me2) [1]. In Arabidopsis thaliana, H3K9me2, catalyzed by the methyltransferase KRYPTONITE (KYP/ SUVH4), is required for maintenance of DNA methylation outside of the standard CG sequence context [3, 4]. Additionally, loss of DNA methylation in the met1 mutant correlates with a loss of H3K9me2 [5, 6]. Here we show that KYP-dependent H3K9me2 is found at non-CG methylation sites in addition to those rich in CG methylation. Furthermore, we show that the SRA domain of KYP binds directly to methylated DNA, and SRA domains with missense mutations found in loss-of-function kyp mutants have reduced binding to methylated DNA in vitro. These data suggest that DNA methylation is required for the recruitment or activity of KYP and suggest a self-reinforcing loop between histone and DNA methylation. Lastly, we found that SRA domains from two Arabidopsis SRA-RING proteins also bind methylated DNA and that the SRA domains from KYP and SRA-RING proteins prefer methylcytosines in different sequence contexts. Hence, unlike the methyl-binding domain (MBD), which binds only methylated-CpG sequences, the SRA domain is a versatile new methyl-DNA-binding motif.", 
"PcG proteins mediate heritable transcriptional silencing by generating and recognizing covalent histone modifications. One conserved PcG complex, PRC2, is composed of several proteins including the histone methyltransferase (HMTase) Ezh2, the WD-repeat protein Eed, and the Zn-finger protein Suz12. Ezh2 methylates histone H3 on lysine 27 (H3K27) [1-4], which serves as an epigenetic mark mediating silencing. H3K27 can be mono-, di-, or trimethylated (1 mH3K27, 2mH3K27, and 3mH3K27, respectively) (5]. Hence, either PRC2 must be regulated so as to add one methyl group to certain nucleosomes but two or three to others, or distinct complexes must be responsible for 1m-, 2m-, and 3mH3K27. Consistent with the latter possibility, 2mH3K27 and 3mH3K27, but not 1mH3K27, are absent in Suz12(-/-) embryos, which lack both Suz12 and Ezh2 protein [6]. Mammalian proteins required for 1mH3K27 have not been identified. Here, we demonstrate that unlike Suz12 and Ezh2, Eed is required not only for 2m- and 3mH3K27 but also global 1mH3K27. These results provide a functionally important distinction between PRC2 complex components and implicate Eed in PRC2-independent histone methylation.", 
"Regulation of gene expression is considered a plausible mechanism of drug addiction, given the stability of behavioural abnormalities that define an addicted state. Among many transcription factors known to influence the addiction process, one of the best characterized is Delta FosB, which is induced in the brain's reward regions by chronic exposure to virtually all drugs of abuse and mediates sensitized responses to drug exposure. Since Delta FosB is a highly stable protein, it represents a mechanism by which drugs produce lasting changes in gene expression long after the cessation of drug use. Studies are underway to explore the detailed molecular mechanisms by which Delta FosB regulates target genes and produces its behavioural effects. We are approaching this question using DNA expression arrays coupled with the analysis of chromatin remodelling-changes in the posttranslational modifications of histones at drug-regulated gene promoters-to identify genes that are regulated by drugs of abuse via the induction of Delta FosB and to gain insight into the detailed molecular mechanisms involved. Our findings establish chromatin remodelling as an important regulatory mechanism underlying drug-induced behavioural plasticity, and promise to reveal fundamentally new insight into how Delta FosB contributes to addiction by regulating the expression of specific target genes in brain reward pathways.", 
"The centromere/kinetochore complex is indispensable for accurate segregation of chromosomes during cell divisions when it serves as the attachment site for spindle microtubules. Centromere identity in metazoans is believed to be governed by epigenetic mechanisms, because the highly repetitive centromeric DNA is neither sufficient nor required for specifying the assembly site of the kinetochore [1-4]. A candidate for an epigenetic mark is the centromere-specific histone H3 variant CENP-A that replaces H3 in alternating blocks of chromatin exclusively in active centromeres [1, 2, 5, 6]. CENP-A acts as an initiator of kinetochore assembly, but the detailed dynamics of the deposition of metazoan CENP-A and of other constitutive kinetochore components are largely unknown [1, 2, 7-10]. Here we show by quantitative fluorescence measurements in living early embryos that functional fluorescent fusion proteins of the Drosophila CENP-A and CENP-C homologs are rapidly incorporated into centromeres during anaphase. This incorporation is independent of ongoing DNA synthesis and pulling forces generated by the mitotic spindle, but strictly coupled to mitotic progression. Thus, our findings uncover a strikingly dynamic behavior of centromere components in anaphase.", 
"That there is a heritable or familial component of susceptibility to chronic non-communicable diseases such as type 2 diabetes, obesity and cardiovascular disease is well established, but there is increasing evidence that some elements of such heritability are transmitted non-genomically and that the processes whereby environmental influences act during early development to shape disease risk in later life can have effects beyond a single generation. Such heritability may operate through epigenetic mechanisms involving regulation of either imprinted or non-imprinted genes but also through broader mechanisms related to parental physiology or behaviour. We review evidence and potential mechanisms for non-genomic transgenerational inheritance of 'lifestyle' disease and propose that the 'developmental origins of disease' phenomenon is a maladaptive consequence of an ancestral mechanism of developmental plasticity that may have had adaptive value in the evolution of generalist species such as Homosapiens. (c) 2007 Wiley Periodicals, Inc.", 
"As is the case with any metaphor, parental effects mean different things to different biologists-from developmental induction of novel phenotypic variation to an evolved adaptation, and from epigenetic transference of essential developmental resources to a stage of inheritance and ecological succession. Such a diversity of perspectives illustrates the composite nature of parental effects that, depending on the stage of their expression and whether they are considered a pattern or a process, combine the elements of developmental induction, homeostasis, natural selection, epigenetic inheritance and historical persistence. Here, we suggest that by emphasizing the complexity of causes and influences in developmental systems and by making explicit the links between development, natural selection and inheritance, the study of parental effects enables deeper understanding of developmental dynamics of life cycles and provides a unique opportunity to explicitly integrate development and evolution. We highlight these perspectives by placing parental effects in a wider evolutionary framework and suggest that far from being only an evolved static outcome of natural selection, a distinct channel of transmission between parents and offspring, or a statistical abstraction, parental effects on development enable evolution by natural selection by reliably transferring developmental resources needed to reconstruct, maintain and modify genetically inherited components of the phenotype. The view of parental effects as an essential and dynamic part of an evolutionary continuum unifies mechanisms behind the origination, modification and historical persistence of organismal form and function, and thus brings us closer to a more realistic understanding of life's complexity and diversity.", 
"Over the past few years we have seen an odd change, or extension, in the use of the word 'epigenetic' when describing matters of gene regulation in eukaryotes. Although it may generally tie that it is not worth arguing over definitions, this is true only insofar as the participants in the discussion know what each other means. I believe the altered use of the term carries baggage from the standard definition that can have misleading implications. Here I wish to probe our use of language in this way, and to show how such a discussion leads to some more general considerations concerning gene regulation.", 
"Polyploidy, or the presence of two or more diploid parental genome sets within an organism, is found to an amazing degree in higher plants. In addition, many plant species traditionally considered to be diploid have recently been demonstrated to have undergone rounds of genome duplication in the past and are now referred to as paleopolyploids. Polyploidy and interspecific hybridisation (with which it is often associated) have long been thought to be important mechanisms of rapid species formation. The widespread occurrence of polyploids, which are frequently found in habitats different from that of their diploid progenitors, would seem to indicate that polyploidy is associated with evolutionary success in terms of the ability to colonise new environmental niches. A flurry of recent genomic studies has provided fresh insights into the potential basis of the phenotypic novelty of polyploid species. Here we review current knowledge of genetic, epigenetic, and transcriptional changes associated with polyploidy in plants and assess how these changes might contribute to the evolutionary success of polyploid plants. We conclude by stressing the need for field-based experiments to determine whether genetic changes associated with polyploidy are indeed adaptive.", 
"The human pathogen Candida albicans can assume either of two distinct cell types, designated ``white'' and ``opaque.'' Each cell type is maintained for many generations; switching between them is rare and stochastic, and occurs without any known changes in the nucleotide sequence of the genome. The two cell types differ dramatically in cell shape, colony appearance, mating competence, and virulence properties. In this work, we investigate the transcriptional circuitry that specifies the two cell types and controls the switching between them. First, we identify two new transcriptional regulators of white-opaque switching, Czf1 and white-opaque regulator 2 (Wor2). Analysis of a large set of double mutants and ectopic expression strains revealed genetic relationships between CZF1, WOR2, and two previously identified regulators of white-opaque switching, WOR1 and EFG1. Using chromatin immunoprecipitation, we show that Wor1 binds the intergenic regions upstream of the genes encoding three additional transcriptional regulators of white-opaque switching (CZF1, EFG1, and WOR2), and also occupies the promoters of numerous white-and opaque-enriched genes. Based on these interactions, we have placed these four genes in a circuit controlling white-opaque switching whose topology is a network of positive feedback loops, with the master regulator gene WOR1 occupying a central position. Our observations indicate that a key role of the interlocking feedback loop network is to stably maintain each epigenetic state through many cell divisions.", 
"Limitation of infarct size is a major goal of therapy for acute coronary syndromes, and research has focused on achieving rapid patency of infarct-related vessels. However, new understandings of epigenetic modifications during ischemia suggest additional targeted approaches that have not been extensively explored. Here, we show that ischemia induces histone deacetylase (HDAC) activity in the heart with deacetyladon of histones H3/4 in vitro and in vivo. We show, utilizing a standard murine model of ischemia-reperfusion, that chemical HDAC inhibitors significantly reduce infarct area, even when delivered 1 h after the ischemic insult. We demonstrate that HDAC inhibitors prevent ischemia-induced activation of gene programs that include hypoxia inducible factor-lot, cell death, and vascular permeability in vivo and in vitro, thus providing potential mechanisms to explain reduced vascular leak and myocardial injury. In vitro, siRNA knockdown experiments implicate HDAC4 as a mediator of the effects in ischemic cardiac myocytes. These results demonstrate that HDAC inhibitors alter the response to ischemic injury in the heart and reduce infarct size, suggesting novel therapeutic approaches for acute coronary syndromes.", 
"Heart valve anomalies are some of the most common congenital heart defects, yet neither the genetic nor the epigenetic forces guiding heart valve development are well understood. When functioning normally, mature heart valves prevent intracardiac retrograde blood flow; before valves develop, there is considerable regurgitation, resulting in reversing (or oscillatory) flows between the atrium and ventricle. As reversing flows are particularly strong stimuli to endothelial cells in culture, an attractive hypothesis is that heart valves form as a developmental response to retrograde blood flows through the maturing heart. Here, we exploit the relationship between oscillatory flow and heart rate to manipulate the amount of retrograde flow in the atrioventricular (AV) canal before and during valvulogenesis, and find that this leads to arrested valve growth. Using this manipulation, we determined that klf2a is normally expressed in the valve precursors in response to reversing flows, and is dramatically reduced by treatments that decrease such flows. Experimentally knocking down the expression of this shear-responsive gene with morpholine antisense oligonucleotides (MOs) results in dysfunctional valves. Thus, klf2a expression appears to be necessary for normal valve formation. This, together with its dependence on intracardiac hemodynamic forces, makes klf2a expression an early and reliable indicator of proper valve development. Together, these results demonstrate a critical role for reversing flows during valvulogenesis and show how relatively subtle perturbations of normal hemodynamic patterns can lead to both major alterations in gene expression and severe valve dysgenesis.", 
"The stunning possibility of reprogramming differentiated somatic cells to express a pluripotent stem cell phenotype (iPS, induced pluripotent stem cell) and the ground state character of pluripotency reveal fundamental features of cell fate regulation that lie beyond existing paradigms. The rarity of reprogramming events appears to contradict the robustness with which the unfathomably complex phenotype of stem cells can reliably be generated. This apparent paradox, however, is naturally explained by the rugged epigenetic landscape with valleys representing preprogrammed', attractor states that emerge from the dynamical constraints of the gene regulatory network. This article provides a pedagogical primer to the fundamental principles of gene regulatory networks as integrated dynamic systems and reviews recent insights in gene expression noise and fate determination, thereby offering a formal framework that may help us to understand why cell fate reprogramming events are inherently rare and yet so robust.", 
"Polycomb group ( PcG) proteins are able to maintain the memory of silent transcriptional states of homeotic genes throughout development. In Drosophila, they form multimeric complexes that bind to specific DNA regulatory elements named PcG response elements ( PREs). To date, few PREs have been identified and the chromosomal distribution of PcG proteins during development is unknown. We used chromatin immunoprecipitation ( ChIP) with genomic tiling path microarrays to analyze the binding profile of the PcG proteins Polycomb ( PC) and Polyhomeotic ( PH) across 10 Mb of euchromatin. We also analyzed the distribution of GAGA factor ( GAF), a sequence-specific DNA binding protein that is found at most previously identified PREs. Our data show that PC and PH often bind to clustered regions within large loci that encode transcription factors which play multiple roles in developmental patterning and in the regulation of cell proliferation. GAF co-localizes with PC and PH to a limited extent, suggesting that GAF is not a necessary component of chromatin at PREs. Finally, the chromosome-association profile of PC and PH changes during development, suggesting that the function of these proteins in the regulation of some of their target genes might be more dynamic than previously anticipated.", 
"Sexual reproduction involves epigenetic reprogramming [1] comprising DNA methylation [2] and histone modifications [3-6]. In addition, dynamics of HISTONE3 (H3) variant H3.3 upon fertilization are conserved in animals, suggesting an essential role [7-9]. In contrast to H3, H3.3 marks actively transcribed regions of the genome and can be deposited in a replication-independent manner [10, 11]. Although H3 variants are conserved in plants, their dynamics during fertilization have remained unexplored. We overcame technical limitations to live imaging of the fertilization process in Arabidopsis thaliana and studied dynamics of the male-gamete-specific H3.3 [12] and the centromeric Histone Three Related 12 (HTR12) [13]. The double-fertilization process in plants produces the zygote and the embryo-nourishing endosperm [14]. We show that the zygote is characterized by replication-independent removal of paternal H3.3 and homogeneous incorporation of parental chromatin complements. In the endosperm, the paternal H3.3 is passively diluted by replication while the paternal chromatin remains segregated apart from the maternal chromatin (gonomery). Hence epigenetic regulations distinguish the two products of fertilization in plants. H3.3-replication-independent dynamics and gonomery also mark the first zygotic divisions in animal species [5, 15]. We thus propose the convergent selection of parental epigenetic imbalance involving H3 variants in sexually reproducing organisms.", 
"Centromeres, the specialized chromatin structures that are responsible for equal segregation of chromosomes at mitosis, are epigenetically maintained by a centromere-specific histone H3 variant (CenH3). However, the mechanistic basis for centromere maintenance is unknown. We investigated biochemical properties of CenH3 nucleosomes from Drosophila melanogaster cells. Cross-linking of CenH3 nucleosomes identifies heterotypic tetramers containing one copy of CenH3, H2A, H2B, and H4 each. Interphase CenH3 particles display a stable association of approximately 120 DNA base pairs. Purified centromeric nucleosomal arrays have typical beads-on-a-string'' appearance by electron microscopy but appear to resist condensation under physiological conditions. Atomic force microscopy reveals that native CenH3-containing nucleosomes are only half as high as canonical octameric nucleosomes are, confirming that the tetrameric structure detected by cross-linking comprises the entire interphase nucleosome particle. This demonstration of stable half-nucleosomes in vivo provides a possible basis for the instability of centromeric nucleosomes that are deposited in euchromatic regions, which might help maintain centromere identity.", 
"It is widely suspected that gene regulatory networks are highly plastic. The rapid turnover of transcription factor binding sites has been predicted on theoretical grounds and has been experimentally demonstrated in closely related species. We combined experimental approaches with comparative genomics to focus on the role of combinatorial control in the evolution of a large transcriptional circuit in the fungal lineage. Our study centers on Mcm1, a transcriptional regulator that, in combination with five cofactors, binds roughly 4% of the genes in Saccharomyces cerevisiae and regulates processes ranging from the cell-cycle to mating. In Kluyveromyces lactis and Candida albicans, two other hemiascomycetes, we find that the Mcm1 combinatorial circuits are substantially different. This massive rewiring of the Mcm1 circuitry has involved both substantial gain and loss of targets in ancient combinatorial circuits as well as the formation of new combinatorial interactions. We have dissected the gains and losses on the global level into subsets of functionally and temporally related changes. One particularly dramatic change is the acquisition of Mcm1 binding sites in close proximity to Rap1 binding sites at 70 ribosomal protein genes in the K. lactis lineage. Another intriguing and very recent gain occurs in the C. albicans lineage, where Mcm1 is found to bind in combination with the regulator Wor1 at many genes that function in processes associated with adaptation to the human host, including the white-opaque epigenetic switch. The large turnover of Mcm1 binding sites and the evolution of new Mcm1-cofactor interactions illuminate in sharp detail the rapid evolution of combinatorial transcription networks.", 
"Background: Heterochromatin is chromosomal material that remains condensed throughout the cell division cycle and silences genes nearby. It is found in almost all eukaryotes, and although discovered (in plants) almost 100 years ago, the mechanism by which heterochromatin is inherited has remained obscure. Heterochromatic silencing and histone H3 lysine-9 methylation (H3K9me2) depend, paradoxically, on heterochromatic transcription and RNA interference (RNAi). Results: Here, we show that heterochromatin protein 1 in fission yeast (Swi6) is lost via phosphorylation of H3 serine 10 (H3S10) during mitosis, allowing heterochromatic transcripts to transiently accumulate in S phase. Rapid processing of these transcripts into small interfering RNA (siRNA) promotes restoration of H3K9me2 and Swi6 after replication when cohesin is recruited. We also show that RNAi in fission yeast is inhibited at high temperatures, providing a plausible mechanism for epigenetic phenomena that depend on replication and temperature, such as vernalization in plants and position effect variegation in animals. Conclusions: These results explain how silent heterochromatin can be transcribed and lead to a model for epigenetic inheritance during replication.", 
"Vernalization promotes flowering in Arabidopsis through epigenetic repression of the floral repressor, FLOWERING LOCUS C (FLC) [1-3]. Vernalization, like other polycomb-mediated repression events [4], occurs in two stages; FLCrepression is established at low temperatures, then maintained during subsequent growth at 22 degrees C [5, 6]. Low temperatures induce VIN3 activity, which is required for changes in histone modifications and the associated FLC repression [3]. Plant polycomb proteins FIE, VRN2, CLF, and SWIN, together with VIN3, form a complex that adds histone H3 lysine 27 methylation at FLC in vernalized plants [2,3,7]. VRN1 and LHP1 are required for maintenance of FLC repression [2, 3, 6, 8]. Tissue must be undergoing cell division during lowtemperature treatments for acceleration of flowering to occur [9, 10]. We show that low-temperature treatments repress FLC in cells that are not mitotically active, but this repression is notfully maintained. Trimethyl-lysine 27 (K27me3), is enriched at the start of the FLC gene during the cold, before spreading across the locus after vernalization. In the absence of DNA replication, K27me3 is added to chromatin at the start of FLC but is removed on return to 22 degrees C. This suggests that DNA replication is essential for maintenance of vernalization-induced repression of FLC.", 
"Ionizing radiation/Bystander effects/Signaling pathways/Plasma membrane/Radiotherapy. A rapidly growing body of experimental evidence indicates that ionizing radiation induces biological effects in non-irradiated bystander cells that have received signals from adjacent or distant irradiated cells. This phenomenon, which has been termed the ionizing radiation-induced bystander effect, challenges the long-standing paradigm that radiation traversal through the nucleus of a cell is a prerequisite to elicit genetic damage or a biological response. Bystander effects have been observed in a number of experimental systems, and cells whose nucleus or cytoplasm is irradiated exert bystander responses. Bystander cells manifest a multitude of biological consequences, such as genetic and epigenetic changes, alterations in gene expression, activation of signal transduction pathways, and delayed effects in their progeny. Several mediating mechanisms have been proposed. These involve gap junction-mediated intercellular communication, secreted soluble factors, oxidative metabolism, plasma membrane-bound lipid rafts, and calcium fluxes. This paper reviews briefly the current knowledge of the bystander effect with a focus on proposed mechanisms. The potential benefit of bystander effects to cancer radiotherapy will also be discussed.", 
"Vernalization, the acceleration of flowering by the prolonged cold of winter, ensures that plants flower in favorable spring conditions. During vernalization in Arabidopsis, cold temperatures repress FLOWERING LOCUS C (FLC) expression [1, 2] in a mechanism involving VERNALIZATION INSENSITIVE 3 (VIN3) [3], and this repression is epigenetically maintained by a Polycomb-like chromatin regulation involving VERNALIZATION 2 (VRN2), a Su(z)12 homolog, VERNALIZATION 1 (VRN1), and LIKE-HETEROCHROMATIN PROTEIN 1 [4-8]. In order to further elaborate how cold repression triggers epigenetic silencing, we have targeted mutations that result in FLC misexpression both at the end of the prolonged cold and after subsequent development. This identified VERNALIZATION 5 (VRN5), a PHD finger protein and homolog of VIN3. Our results suggest that during the prolonged cold, VRN5 and VIN3 form a heterodimer necessary for establishing the vernalization-induced chromatin modifications, histone deacetylation, and H3 lysine 27 trimethylation required for the epigenetic silencing of FLC. Double mutant and FLCmisexpression analyses reveal additional VRN5 functions, both FLC-dependent and -independent, and indicate a spatial complexity to FLC epigenetic silencing with VRN5 acting as a common component in multiple pathways.", 
"It is usually thought that the development of complex organisms is controlled by protein regulatory factors and morphogenetic signals exchanged between cells and differentiating tissues during ontogeny. However, it is now evident that the majority of all animal genomes is transcribed, apparently in a developmentally regulated manner, suggesting that these genomes largely encode RNA machines and that there may be a vast hidden layer of RNA regulatory transactions in the background. I propose that the epigenetic trajectories of differentiation and development are primarily programmed by feedforward RNA regulatory networks and that most of the information required for multicellular development is embedded in these networks, with cell-cell signalling required to provide important positional information and to correct stochastic errors in the endogenous RNA-directed program.", 
"Handedness and cerebral asymmetry are commonly assumed to be uniquely human, and even defining characteristics of our species. This is increasingly refuted by the evidence of behavioural asymmetries in non-human species. Although complex manual skill and language are indeed unique to our species and are represented asymmetrically in the brain, some non-human asymmetries appear to be precursors, and others are shared between humans and non-humans. In all behavioural and cerebral asymmetries so far investigated, a minority of individuals reverse or negate the dominant asymmetry, suggesting that such asymmetries are best understood in the context of the overriding bilateral symmetry of the brain and body, and a trade-off between the relative advantages and disadvantages of symmetry and asymmetry. Genetic models of handedness, for example, typically postulate a gene with two alleles, one disposing towards right-handedness and the other imposing no directional influence. There is as yet no convincing evidence as to the location of this putative gene, suggesting that several genes may be involved, or that the gene may be monomorphic with variations due to environmental or epigenetic influences. Nevertheless, it is suggested that, in behavioural, neurological and evolutionary terms, it may be more profitable to examine the degree rather than the direction of asymmetry.", 
"Background: Epigenetic regulation by diverse classes of small RNAs is mediated by the highly conserved Argonaute/Piwi family of proteins. Although Argonautes are broadly expressed, the Piwi subfamily primarily functions in the germ line. Piwi proteins are associated with germline-specific ribonucleoprotein (RNP) granules in Drosophila, zebrafish, and mouse. Depending on the species and on the specific family member, Piwis play important roles in spermatogenesis and/or in maintaining germ cell and stem cell totipotency. Piwis bind to a newly discovered class of small RNAs, called piRNAs. C. elegans contains a large set of Argonaute/Piwi-related proteins, including two closely related to piwi called prg-1 and prg-2. The function of prg-1 and prg-2 and whether piRNAs exist in C. elegans is unknown. Results: Here, we demonstrate that the Piwi-like protein PRG-1 is localized to P granules in germ cells entering spermatogenesis and is required for successful spermatogenesis. Loss of prg-1 causes a marked reduction in expression of a subset of mRNAs expressed during spermatogenesis, and prg-1 mutant sperm exhibit extensive defects in activation and fertilization. Moreover, prg-1 activity is required for the presence of the small RNAs called 21 U-RNAs. Conclusions: Our data suggest that PRG-1 promotes expression, processing, or stability of 21 U-RNAs, which, in turn or in concert with PRG-1, promote proper expression of spermatogenesis transcripts.", 
"Background: Adipose tissues serve not only as a store for energy in the form of lipid, but also as endocrine tissues that regulates metabolic activities of the organism by secreting various kinds of hormones. Peroxisome proliferator activated receptor. (PPAR gamma) is a key regulator of adipocyte differentiation that induces the expression of adipocyte-specific genes in preadipocytes and mediates their differentiation into adipocytes. Furthermore, PPAR gamma has an important role to maintain the physiological function of mature adipocyte by controlling expressions of various genes properly. Therefore, any reduction in amount and activity of PPAR gamma is linked to the pathogenesis of metabolic syndrome. Results: In this study, we investigated the contribution of epigenetic transcriptional regulatory mechanisms, such as DNA methylation, to the expression of the PPAR gamma gene, and further evaluated the contribution of such epigenetic regulatory mechanisms to the pathogenesis of metabolic syndrome. In 3T3-L1 preadipocytes, the promoter of the PPAR gamma 2 gene was hypermethylated, but was progressively demethylated upon induction of differentiation, which was accompanied by an increase of mRNA expression. Moreover, treatment of cells with 5'-aza-cytideine, an inhibitor of DNA methylation, increased expression of the PPAR gamma gene in a dose-dependent manner. Methylation in vitro of a PPAR gamma promoter-driven reporter construct also repressed the transcription of a downstream reporter gene. These results suggest that the expression of the PPAR gamma gene is inhibited by methylation of its promoter. We next compared the methylation status of the PPAR gamma promoters in adipocytes from wild-type (WT) mice with those from two diabetic mouse models: +Lepr(db)/+Lepr(db) and diet-induced obesity mice. Interestingly, we found increased methylation of the PPAR gamma promoter in visceral adipose tissues (VAT) of the mouse models of diabetes, compared to that observed in wild-type mice. We observed a concomitant decrease in the level of PPAR gamma mRNA in the diabetic mice compared to the WT mice. Conclusion: We conclude that the expression of PPAR gamma gene is regulated by DNA methylation of its promoter region and propose that reduced expression of PPAR gamma owing to DNA methylation in adipocytes of the VAT may contribute to the pathogenesis of metabolic syndrome.", 
"Developing embryos exhibit a robust capability to reduce phenotypic variations that occur naturally or as a result of experimental manipulation. This reduction in variation occurs by an epigenetic mechanism called canalization, a phenomenon which has resisted understanding because of a lack of necessary molecular data and of appropriate gene regulation models. In recent years, quantitative gene expression data have become available for the segment determination process in the Drosophila blastoderm, revealing a specific instance of canalization. These data show that the variation of the zygotic segmentation gene expression patterns is markedly reduced compared to earlier levels by the time gastrulation begins, and this variation is significantly lower than the variation of the maternal protein gradient Bicoid. We used a predictive dynamical model of gene regulation to study the effect of Bicoid variation on the downstream gap genes. The model correctly predicts the reduced variation of the gap gene expression patterns and allows the characterization of the canalizing mechanism. We show that the canalization is the result of specific regulatory interactions among the zygotic gap genes. We demonstrate the validity of this explanation by showing that variation is increased in embryos mutant for two gap genes, Kruppel and knirps, disproving competing proposals that canalization is due to an undiscovered morphogen, or that it does not take place at all. In an accompanying article in PLoS Computational Biology (doi:10.1371/journal:pcbi.1000303), we show that cross regulation between the gap genes causes their expression to approach dynamical attractors, reducing initial variation and providing a robust output. These results demonstrate that the Bicoid gradient is not sufficient to produce gap gene borders having the low variance observed, and instead this low variance is generated by gap gene cross regulation. More generally, we show that the complex multigenic phenomenon of canalization can be understood at a quantitative and predictive level by the application of a precise dynamical model.", 
"Fertilization in flowering plants initiates the development of the embryo and endosperm, which nurtures the embryo. A few genes subjected to imprinting are expressed in endosperm from their maternal allele, while their paternal allele remains silenced [1-3]. Imprinting of the FWA gene involves DNA methylation [4]. Mechanisms controlling imprinting of the Polycomb group (Pc-G) gene MEDEA (MEA) [5] are not yet fully understood [6-10]. Here we report that MEA imprinting is regulated by histone methylation. This epigenetic chromatin modification is mediated by several Pc-G activities during the entire plant life cycle. We show that Pc-G complexes maintain MEA transcription silenced throughout vegetative life and male gametogenesis. In endosperm, the maternal allele of MEA encodes an essential component of a Pc-G complex, which maintains silencing of the paternal MEA allele. Hence, we conclude that a feedback loop controls MEA imprinting. This feedback loop ensures a complete maternal control of MEA expression from both parental alleles and might have provided a template for evolution of imprinting in plants.", 
"Vertebrate hearts depend on highly specialized cardiomyocytes that form the cardiac conduction system (CCS) to coordinate chamber contraction and drive blood efficiently and unidirectionally throughout the organism. Defects in this specialized wiring system can lead to syncope and sudden cardiac death. Thus, a greater understanding of cardiac conduction development may help to prevent these devastating clinical outcomes. Utilizing a cardiac-specific fluorescent calcium indicator zebrafish transgenic line, Tg(cmlc2:gCaMP)(s878), that allows for in vivo optical mapping analysis in intact animals, we identified and analyzed four distinct stages of cardiac conduction development that correspond to cellular and anatomical changes of the developing heart. Additionally, we observed that epigenetic factors, such as hemodynamic flow and contraction, regulate the fast conduction network of this specialized electrical system. To identify novel regulators of the CCS, we designed and performed a new, physiology-based, forward genetic screen and identified for the first time, to our knowledge, 17 conduction-specific mutations. Positional cloning of hobgoblin(s634) revealed that tcf2, a homeobox transcription factor gene involved in mature onset diabetes of the young and familial glomerulocystic kidney disease, also regulates conduction between the atrium and the ventricle. The combination of the Tg(cmlc2:gCaMP)(s878) line/in vivo optical mapping technique and characterization of cardiac conduction mutants provides a novel multidisciplinary approach to further understand the molecular determinants of the vertebrate CCS.", 
"Bacterial LPS triggers dramatic changes in gene expression in macrophages. We show here that LPS regulated several members of the histone deacetylase (HDAC) family at the mRNA level in murine bone marrow-derived macrophages (BMM). LPS transiently repressed, then induced a number of HDACs (Hdac-4, 5, 7) in BMM, whereas Hdac-1 mRNA was induced more rapidly. Treatment of BMM with trichostatin A (TSA), an inhibitor of HDACs, enhanced LPS-induced expression of the Cox-2, Cxcl2, and Ifit2 genes. In the case of Cox-2, this effect was also apparent at the promoter level. Overexpression of Hdac-8 in RAW264 murine macrophages blocked the ability of LPS to induce Cox-2 mRNA. Another class of LPS-inducible genes, which included Ccl2, Ccl7, and Edn1, was suppressed by TSA, an effect most likely mediated by PU.1 degradation. Hence, HDACs act as potent and selective negative regulators of proinflammatory gene expression and act to prevent excessive inflammatory responses in macrophages.", 
"Cytoadherance of Plasmodium falciparum-infected erythrocytes in the brain, organs and peripheral microvasculature is linked to morbidity and mortality associated with severe malaria. Parasite-derived P. falciparum Erythrocyte Membrane Protein 1 (PfEMP1) molecules displayed on the erythrocyte surface are responsible for cytoadherance and undergo antigenic variation in the course of an infection. Antigenic variation of PfEMP1 is achieved by in situ switching and mutually exclusive transcription of the var gene family, a process that is controlled by epigenetic mechanisms. Here we report characterisation of the P. falciparum silent information regulator's A and B (PfSir2A and PfSir2B) and their involvement in mutual exclusion and silencing of the var gene repertoire. Analysis of P. falciparum parasites lacking either PfSir2A or PfSir2B shows that these NAD(+)-dependent histone deacetylases are required for silencing of different var gene subsets classified by their conserved promoter type. We also demonstrate that in the absence of either of these molecules mutually exclusive expression of var genes breaks down. We show that var gene silencing originates within the promoter and PfSir2 paralogues are involved in cis spreading of silenced chromatin into adjacent regions. Furthermore, parasites lacking PfSir2A but not PfSir2B have considerably longer telomeric repeats, demonstrating a role for this molecule in telomeric end protection. This work highlights the pivotal but distinct role for both PfSir2 paralogues in epigenetic silencing of P. falciparum virulence genes and the control of pathogenicity of malaria infection.", 
"Background: The telomere is a specialized heterochromatin conserved among eukaryotes. However, it remains unknown how heterochromatin protein 1 (HP1) is recruited to telomeres and how telomere heterochromatin is formed. In fission yeast, the RNAi (RNA interference)-RITS (RNA-induced initiation of transcriptional silencing) pathway initiates heterochromatin formation at the centromeres and the silent mat locus by using common DNA sequences, the dg and dh repeats, as the templates for small interfering RNA (siRNA). Results: We found that telomeric repeats are sufficient for the establishment of Swi6 (a fission-yeast HP1 homolog) heterochromatin, and the establishment requires Taz1, a telomere binding protein of the TRF family. Additionally, Swi6 heterochromatin is established by a part of the subtelomere that contains sequences highly homologous to that of the dh repeat, and it is strikingly destabilized by the deletion of both Taz1 and RNAi-RITS. Transcripts from the telomeric dh-homologous region were specifically associated with RITS, and deletion of the telomeric dh-homologous region showed the phenotype similar to that of the rnai mutant in terms of the telomeric silencing, indicating that the RNAi-RITS pathway acts at the telomeric dh-homologous region to establish Swi6 heterochromatin. Furthermore, we found that Taz1 establishes Swi6 heterochromatin independently of the telomeric repeats and the RNAi-RITS pathway at the subtelomeres. Conclusion: The telomere heterochromatin is regulated by at least two factors: One is Taz1, which is telomere specific, and the other is RNAi-RITS, which is commonly used at the constitutive heterochromatin regions.", 
"Imprinted genes are expressed either from the maternally or paternally inherited copy only, and they play a key role in regulating complex biological processes, including offspring development and mother-offspring interactions. There are several competing theories attempting to explain the evolutionary origin of this monoallelic pattern of gene expression, but a prevailing view has emerged that holds that genomic imprinting is a consequence of conflict between maternal and paternal gene copies over maternal investment. However, many imprinting patterns and the apparent overabundance of maternally expressed genes remain unexplained and may be incompatible with current theory. Here we demonstrate that sole expression of maternal gene copies is favored by natural selection because it increases the adaptive integration of offspring and maternal genomes, leading to higher offspring fitness. This novel coadaptation theory for the evolution of genomic imprinting is consistent with results of recent studies on epigenetic effects, and it provides a testable hypothesis for the origin of previously unexplained major imprinting patterns across different taxa. In conjunction with existing hypotheses, our results suggest that imprinting may have evolved due to different selective pressures at different loci.", 
"The origin of novel traits is what draws many to evolutionary biology, yet our understanding of the mechanisms that underlie the genesis of novelty remains limited. Here I review definitions of novelty including its relationship to homology. I then discuss how ontogenetic perspectives may allow us to move beyond current roadblocks in our understanding of the mechanics of innovation. Specifically, I explore the roles of canalization, plasticity and threshold responses during development in generating a reservoir of cryptic genetic variation free to drift and accumulate in natural populations. Environmental or genetic perturbations that exceed the buffering capacity of development can then release this variation, and, through evolution by genetic accommodation, result in rapid diversification, recurrence of lost phenotypes as well as the origins of novel features. I conclude that, in our quest to understand the nature of innovation, the nature of development deserves to take center stage.", 
"Many DNA hypermethylated and epigenetically silenced genes in adult cancers are Polycomb group (PcG) marked in embryonic stem (ES) cells. We show that a large region upstream (similar to 30 kb) of and extending similar to 60 kb around one such gene, GATA-4, is organized-in Tera-2 undifferentiated embryonic carcinoma (EC) cells-in a topologically complex multi-loop conformation that is formed by multiple internal long-range contact regions near areas enriched for EZH2, other PcG proteins, and the signature PcG histone mark, H3K27me3. Small interfering RNA (siRNA)-mediated depletion of EZH2 in undifferentiated Tera-2 cells leads to a significant reduction in the frequency of long-range associations at the GATA-4 locus, seemingly dependent on affecting the H3K27me3 enrichments around those chromatin regions, accompanied by a modest increase in GATA-4 transcription. The chromatin loops completely dissolve, accompanied by loss of PcG proteins and H3K27me3 marks, when Tera-2 cells receive differentiation signals which induce a similar to 60-fold increase in GATA-4 expression. In colon cancer cells, however, the frequency of the long-range interactions are increased in a setting where GATA-4 has no basal transcription and the loops encompass multiple, abnormally DNA hypermethylated CpG islands, and the methyl-cytosine binding protein MBD2 is localized to these CpG islands, including ones near the gene promoter. Removing DNA methylation through genetic disruption of DNA methyltransferases (DKO cells) leads to loss of MBD2 occupancy and to a decrease in the frequency of long-range contacts, such that these now more resemble those in undifferentiated Tera-2 cells. Our findings reveal unexpected similarities in higher order chromatin conformation between stem/precursor cells and adult cancers. We also provide novel insight that PcG-occupied and H3K27me3-enriched regions can form chromatin loops and physically interact in cis around a single gene in mammalian cells. The loops associate with a poised, low transcription state in EC cells and, with the addition of DNA methylation, completely repressed transcription in adult cancer cells.", 
"Background: Centromeres are cis-acting chromosomal domains that direct kinetochore formation, enabling faithful chromosome segregation. Centromeric regions of higher eukaryotes are structurally complex, consisting of various epigenetically modified chromatin types including specialized chromatin at the kinetochore itself, pericentromeric heterochromatin, and flanking euchromatin. Although the features necessary for the establishment and maintenance of discrete chromatin domains remain poorly understood, two models have been proposed based either on the passive convergence of competing activities involved in individual domain formation or, alternatively, on the action of specific genomic sequences and associated proteins to actively block the propagation of one chromatin type into another. Results: Functional analysis of centromeric sequences located at the intersection of Schizosaccharomyces pombe central core chromatin and outer repeat heterochromatin identified a chromatin barrier that contains a transfer RNA (tRNA) gene. Deletion or modification of the barrier sequences result in the propagation of pericentromeric heterochromatin beyond its normal boundary. The tRNA gene is transcriptionally active, and barrier activity requires sequences necessary for RNA polymerase III transcription. Moreover, absence of the barrier results in abnormal meiotic chromosome segregation. Conclusions: The identification of DNA sequences with chromatin barrier activity at the fission yeast centromere provides a model for establishment of centromeric chromatin domains in higher eukaryotes.", 
"Tandem repeat sequences are frequently associated with gene silencing phenomena. The Arabidopsis thaliana FWA gene contains two tandem repeats and is an efficient target for RNA-directed de novo DNA methylation when it is transformed into plants. We showed that the FWA tandem repeats are necessary and sufficient for de novo DNA methylation and that repeated character rather than intrinsic sequence is likely important. Endogenous FWA can adopt either of two stable epigenetic states: methylated and silenced or unmethylated and active. Surprisingly, we found small interfering RNAs ( siRNAs) associated with FWA in both states. Despite this, only the methylated form of endogenous FWA could recruit further RNA-directed DNA methylation or cause efficient de novo methylation of transgenic FWA. This suggests that RNA-directed DNA methylation occurs in two steps: first, the initial recruitment of the siRNA-producing machinery, and second, siRNA-directed DNA methylation either in cis or in trans. The efficiency of this second step varies depending on the nature of the siRNA-producing locus, and at some loci, it may require preexisting chromatin modifications such as DNA methylation itself. Enhancement of RNA-directed DNA methylation by pre-existing DNA methylation could create a self-reinforcing system to enhance the stability of silencing. Tandem repeats throughout the Arabidopsis genome produce siRNAs, suggesting that repeat acquisition may be a general mechanism for the evolution of gene silencing.", 
"Expression of imprinted genes is restricted to a single parental allele as a result of epigenetic regulation - DNA methylation and histone modifications. Igf2/H19 is a reciprocally imprinted locus exhibiting paternal Igf2 and maternal H19 expression. Their expression is regulated by a paternally methylated imprinting control region ( ICR) located between the two genes. Although the de novo DNA methyltransferases have been shown to be necessary for the establishment of ICR methylation, the mechanism by which they are targeted to the region remains unknown. We demonstrate that CTCFL/BORIS, a paralog of CTCF, is an ICR-binding protein expressed during embryonic male germ cell development, coinciding with the timing of ICR methylation. PRMT7, a protein arginine methyltransferase with which CTCFL interacts, is also expressed during embryonic testis development. Symmetrical dimethyl arginine 3 of histone H4, a modification catalyzed by PRMT7, accumulates in germ cells during this developmental period. This modified histone is also found enriched in both H19 ICR and Gtl2 differentially methylated region ( DMR) chromatin of testis by chromatin immunoprecipitation ( ChIP) analysis. In vitro studies demonstrate that CTCFL stimulates the histone-methyltransferase activity of PRMT7 via interactions with both histones and PRMT7. Finally, H19 ICR methylation is demonstrated by nuclear co-injection of expression vectors encoding CTCFL, PRMT7, and the de novo DNA methyltransferases, Dnmt3a, -b and -L, in Xenopus oocytes. These results suggest that CTCFL and PRMT7 may play a role in male germline imprinted gene methylation.", 
"Plant cells grown in culture exhibit genetic and epigenetic instability. Using a combination of chromatin immunoprecipitation and DNA methylation profiling on tiling microarrays, we have mapped the location and abundance of histone and DNA modifications in a continuously proliferating, dedifferentiated cell suspension culture of Arabidopsis. We have found that euchromatin becomes hypermethylated in culture and that a small percentage of the hypermethylated genes become associated with heterochromatic marks. In contrast, the heterochromatin undergoes dramatic and very precise DNA hypomethylation with transcriptional activation of specific transposable elements (TEs) in culture. High throughput sequencing of small interfering RNA (siRNA) revealed that TEs activated in culture have increased levels of 21-nucleotide (nt) siRNA, sometimes at the expense of the 24-nt siRNA class. In contrast, TEs that remain silent, which match the predominant 24-nt siRNA class, do not change significantly in their siRNA profiles. These results implicate RNA interference and chromatin modification in epigenetic restructuring of the genome following the activation of TEs in immortalized cell culture.", 
"The effects of nonmutagenic environmental exposures can sometimes be transmitted for several generations, suggesting transgenerational inheritance of induced epigenetic variation. Methyl donor supplementation of female mice during pregnancy induces CpG hypermethylation at the agouti viable yellow ( A(vy)) allele in A(vy)/a offspring. Epigenetic inheritance occurs at A(vy); when passed through the female germ line, A(vy) epigenotype is not completely reset. We therefore tested whether diet-induced epigenetic alterations at A(vy) are inherited transgenerationally. Female A(vy)/a mice were weaned onto either control ( n = 6) or a methyl-supplemented diet ( n = 5). These F0 dams were mated with a/a males. All F1 and F2 A(vy)/a females were weaned onto the same diet as their mothers, then mated with a/a males. F1, F2, and F3 A(vy)/a offspring were classified for coat color, an indicator of A(vy) methylation. In total, 62 F1, 98 F2, and 209 F3 A(vy)/a mice were studied. As expected, average A(vy)/a coat color was darker in the supplemented group ( P< 0.01). However, there was no cumulative effect of supplementation across successive generations. These results suggest that, in the female germ line, diet-induced A(vy) hypermethylation occurs in the absence of additional epigenetic modifications that normally confer transgenerational epigenetic inheritance at the locus. - Waterland, R. A., Travisano, M., Tahiliani, K. G. Diet-induced hypermethylation at agouti viable yellow is not inherited transgenerationally through the female.", 
"The enzyme-catalyzed acetylation of the N-terminal tail domains of core histones provides a rich potential source of epigenetic information. This may be used both to mediate transient changes in transcription, through modification of promoter-proximal nucleosomes, and for the longer-term maintenance and modulation of patterns of gene expression. The latter may be achieved by setting specific patterns of histone acetylation, perhaps involving acetylation of particular lysine residues, across relatively large chromatin domains. The histone acetylating and deacetylating enzymes (HATs and HDACs, respectively) can be targeted to specific regions of the genome and show varying degrees of substrate specificity, properties that are consistent with a role in maintaining a dynamic, acetylation-based epigenetic code. The code may be read (ie. exert a functional effect) either through non-histone proteins that bind in an acetylation-dependent manner, or through direct effects on chromatin structure. Recent evidence raises the interesting possibility that an acetylation-based code may operate through both mitosis and meiosis, providing a possible mechanism for germ-line transmission of epigenetic changes. BioEssays 22:836-845, 2000. (C) 2000 John Wiley & Sons, Inc.", 
"DNA methylation is essential for the control of a number of biological mechanisms in mammals [1]. Mammalian development is accompanied by two major waves of genome-wide demethylation and remethylation: one during germ-cell development and the other after fertilisation [2-7]. Most previous studies have suggested that the genome-wide demethylation observed after fertilisation occurs passively, that is, by the lack of maintenance methylation following DNA replication and cell division [6,7], although one other study has reported that replication-independent demethylation may also occur during early embryogenesis [8]. Here, we report that genes that are highly methylated in sperm are rapidly demethylated in the zygote only hours after fertilisation, before the first round of DNA replication commences. By contrast, the oocyte-derived maternal alleles are unaffected by this reprogramming. They either remain methylated after fertilisation or become further methylated de novo. These results provide the first direct evidence for active demethylation of single-copy genes in the mammalian zygote and, moreover, reveal a striking asymmetry in epigenetic methylation reprogramming. Whereas paternally (sperm)-derived sequences are exposed to putative active demethylases in the oocyte cytoplasm, maternally (oocyte)-derived sequences are protected from this reaction. These results, whose generality is supported by findings of Mayer et al. [9], have important implications for the establishment of biparental genetic totipotency after fertilisation, the establishment and maintenance of genomic imprinting, and the reprogramming of somatic cells during cloning.", 
"Proper DNA methylation patterning requires the complementary processes of de novo methylation (the initial methylation of unmethylated DNA sequences) and maintenance methylation (the faithful replication of preexisting methylation). Arabidopsis has two types of methyltransferases with demonstrated maintenance activity: MET1, which maintains CpG methylation [1-3] and is homologous to mammalian DNMT1, and CHROMOMETHYLASE 3 (CMT3), which maintains CpNpG (N = A, T, C, or G) methylation [3,4] and is unique to the plant kingdom. Here we describe loss-of-function mutations in the Arabidopsis DOMAINS REARRANGED METHYLASE (DRM) genes [5] and provide evidence that they encode de novo methyltransferases. drm1 drm2 double mutants retained preexisting CpG methylation at the endogenous FWA locus but blocked de novo CpG methylation that is normally associated with FWA transgene silencing. Furthermore, drm1 drm2 double mutants blocked de novo CpNpG and asymmetric methylation and gene silencing of the endogenous SUPERMAN (SUP) gene, which is normally triggered by an inverted SUP repeat. However, drm1 drm2 double mutants did not show reactivation of previously established SUPERMAN epigenetic silenced alleles. Thus, drm mutants prevent the establishment but not the maintenance of gene silencing at FWA and SUP, suggesting that the DRMs encode the major de novo methylation enzymes affecting these genes.", 
"The conserved histone variant H2A.Z functions in euchromatin to antagonize the spread of heterochromatin. The mechanism by which histone H2A is replaced by H2A.Z in the nucleosome is unknown. We identified a complex containing 13 different polypeptides associated with a soluble pool of H2A.Z in Saccharomyces cerevisiae. This complex was designated SWR1-Com in reference to the Swr1p subunit, a Swi2/Snf2-paralog. Swr1p and six other subunits were found only in SWR1-Com, whereas six other subunits were also found in the NuA4 histone acetyltransferase and/or the Ino80 chromatin remodeling complex. H2A.Z and SWR1 were essential for viability of cells lacking the EAF1 component of NuA4, pointing to a close functional connection between these two complexes. Strikingly, chromatin immunoprecipitation analysis of cells lacking Swr1p, the presumed ATPase of the complex, revealed a profound defect in the deposition of H2A.Z at euchromatic regions that flank the silent mating type cassette HMR and at 12 other chromosomal sites tested. Consistent with a specialized role for Swr1p in H2A.Z deposition, the majority of the genome-wide transcriptional defects seen in swr1Delta cells were also found in htz1Delta cells. These studies revealed a novel role for a member of the ATP-dependent chromatin remodeling enzyme family in determining the region-specific histone subunit composition of chromatin in vivo and controlling the epigenetic state of chromatin. Metazoan orthologs of Swr1p (Drosophila Domino; human SRCAP and p400) may have analogous functions.", 
"During differentiation, somatic nuclei acquire highly specialized DNA and chromatin modifications, which are thought to result in cellular memory of the differentiated state [1]. Upon somatic nuclear transfer into oocytes, the donor nucleus may have to undergo reprogramming of these epigenetic marks in order to achieve totipotency. This may involve changes in epigenetic features similar to those that occur in normal embryos during early development [2-6]. However, there is accumulating evidence that epigenetic reprogramming is severely deficient in cloned embryos [712]. Several reports reveal inefficient demethylation and inappropriate reestablishment of DNA methylation in quantitative and qualitative patterns on somatic nuclear transfer [7-12]. Here we examine histone H3 lysine 9 (H3-K9) methylation and acetylation in normal embryos and in those created by somatic nuclear transfer. We find that H3-K9 methylation is reprogrammed in parallel with DNA methylation in normal embryos. However, the majority of cloned embryos exhibit H3-K9 hypermethylation associated with DNA hypermethylation, suggesting a genome-wide failure of reprogramming. Strikingly, the precise epigenotype in cloned embryos depends on the donor cell type, and the proportion of embryos with normal epigenotypes correlates closely with the proportion developing to the blastocyst stage. These results suggest a mechanistic link between DNA and histone methylation in the mammalian embryo and reveal an association between epigenetic marks and developmental potential of cloned embryos.", 
"The central dogma of biology holds that genetic information normally flows from DNA to RNA to protein. As a consequence it has been generally assumed that genes generally code for proteins, and that proteins fulfil not only most structural and catalytic but also most regulatory functions, in all cells, from microbes to mammals. However, the latter may not be the case in complex organisms. A number of startling observations about the extent of non-protein-coding RNA (ncRNA) transcription in the higher eukaryotes and the range of genetic and epigenetic phenomena that are RNA-directed suggests that the traditional view of the structure of genetic regulatory systems in animals and plants may be incorrect. ncRNA dominates the genomic output of the higher organisms and has been shown to control chromosome architecture, mRNA turnover and the developmental timing of protein expression, and may also regulate transcription and alternative splicing. This paper re-examines the available evidence and suggests a new framework for considering and understanding the genomic programming of biological complexity, autopoletic development and phenotypic variation. BioEssays 25:930-939,2003. (C) 2003 Wiley Periodicals, Inc.", 
"Background: The heterochromatin of many eukaryotes is marked by both DNA methylation and histone H3 lysine 9 (H3-K9) methylation, though the exact relationship between these epigenetic modifications is unknown. In Neurospora, H3-K9 methylation is required for the maintenance of all known DNA methylation. In Arabidopsis, H3-K9 methylation directs some of the CpNpG and asymmetric methylation. However, it is not known in any organism whether DNA methylation may also direct histone H3 methylation. Results: Using chromatin immunoprecipitation (ChIP) assays, we show that Arabidopsis heterochromatin is associated with H3-K9 methylation. This histone methylation is dependent on the KRYPTONITE and DDM1 genes (SU[VAR]3-9 and SWI2/SNF2 homologs, respectively). We also find that a decrease in DNA methylation does not directly cause a loss of H3-K9 methylation. Instead, a decrease in H3-K9 methylation is only seen at loci where transcription is derepressed. Conclusions: We conclude that DNA methylation does not control the methylation of histone H3-K9. We propose that loss of H3-K9 methylation is due to transcriptional reactivation, coupled with deposition of unmethylated nucleosomes. These findings are consistent with recent observations of DNA replication-independent deposition of histone H3.3 in Drosophila. Our results also suggest that, in Arabidopsis, DNA methylation is sufficient for gene silencing, but H3-K9 methylation is not.", 
"Heritable, but reversible, changes in transposable element activity were first observed in maize by Barbara McClintock in the 1950s. More recently, transposon silencing has been associated with DNA methylation, histone H3 lysine-9 methylation (H3mK9), and RNA interference (RNAi). Using a genetic approach, we have investigated the role of these modifications in the epigenetic regulation and inheritance of six Arabidopsis transposons. Silencing of most of the transposons is relieved in DNA methyltransferase (met1), chromatin remodeling ATPase (ddm1), and histone modification (sil1) mutants. In contrast, only a small subset of the transposons require the H3mK9 methyltransferase KRYPTONITE, the RNAi gene ARGONAUTE1, and the CXG methyltransferase CHROMOMETHYLASE3. In crosses to wildtype plants, epigenetic inheritance of active transposons varied from mutant to mutant, indicating these genes differ in their ability to silence transposons. According to their pattern of transposon regulation, the mutants can be divided into two groups, which suggests that there are distinct, but interacting, complexes or pathways involved in transposon silencing. Furthermore, different transposons tend to be susceptible to different forms of epigenetic regulation.", 
"Background: The Ras-GTPase controls cell fate decisions through the binding of an array of effector molecules, such as Raf and PI 3-kinase, in a GTP-dependent manner. NORE1, a noncatalytic polypeptide, binds specifically to Ras-GTP and to several other Ras-like GTPases. NORE is homologous to the putative tumor suppressor RASSF1 and to the Caenorhabditis elegans polypeptide T24F1.3. Results: We find that all three NORE-related polypeptides bind selectively to the proapoptotic protein kinase MST1, a member of the Group 11 GC kinases. Endogenous NORE and MST1 occur in a constitutive complex in vivo that associates with endogenous Ras after serum stimulation. Targeting recombinant MST1 to the membrane, either through NORE or myristoylation, augments the apoptotic efficacy of MST1. Overexpression of constitutively active Ki-RasG12V promotes apoptosis in a variety of cell lines; Ha-RasG12V is a much less potent proapoptotic agent; however, a Ha-RasG12V effector loop mutant (E37G) that binds NORE, but not Raf or PI 3-kinase, exhibits proapoptotic efficacy approaching that of Ki-RasG12V. The apoptotic action of both Ki-RasG12V and Ha-RasG12V, E37G is suppressed by overexpression of the MST1 carboxy-terminal noncatalytic segment or by the NORE segment that binds MST1. Conclusions: MST1 is a phylogenetically conserved partner of the NORE/RASSF polypeptide family, and the NORE-MST1 complex is a novel Ras effector unit that mediates the apoptotic effect of Ki-RasG12V.", 
"Full-term development has now been achieved in several mammalian species by transfer of somatic nuclei into enucleated oocytes [1, 2]. Although a high proportion of such reconstructed embryos can evolve until the blastocyst stage, only a few percent develop into live offspring, which often exhibit developmental abnormalities [3, 4]. Regulatory epigenetic markers such as DNA methylation are imposed on embryonic cells as normal development proceeds, creating differentiated cell states. Cloned embryos require the erasure of their somatic epigenetic markers so as to regain a totipotent state [5]. Here we report on differences in the dynamics of chromosome methylation between cloned and normal bovine embryos before implantation. We show that cloned embryos fail to reproduce distinguishable parental-chromosome methylation patterns after fusion and maintain their somatic pattern during subsequent stages, mainly by a highly reduced efficiency of the passive demethylation process. Surprisingly, chromosomes appear constantly undermethylated on euchromatin in morulae and blastocysts, while centromeric heterochromatin remains more methylated than that of normal embryos. We propose that the abnormal time-dependent methylation events spanning the preimplantation development of clones may significantly interfere with the epigenetic reprogramming, contributing to the high incidence of physiological anomalies occurring later during pregnancy or after clone birth.", 
"Background: The association between DNA methylation and gene silencing has long been recognized; however, signals that initiate de novo methylation are largely unknown. In plants, recognition of RNAs that are inducers of posttranscriptional gene silencing (PTGS) can result in sequence-specific DNA methylation, and the aim of this work was to investigate whether heritable epigenetic changes can occur by this mechanism and if the Met1 methyltransferase is required. Results: RNA-directed DNA methylation (RdDM) was initiated in 35S-GFP transgenic plants following infection with plant RNA viruses modified to carry portions of either the 35S promoter or the GFP coding region. Targeting of the promoter sequence resulted in both methylation and transcriptional gene silencing (TGS) that was inherited independently of the RNA trigger. Targeting the coding region also resulted in methylation; however, this was not inherited, Expression of Met1 was suppressed in order to investigate its role in initiation and maintenance of RdDM. Initiation of RdDM was found to be Met1-independent, whereas maintenance of methylation and TGS in the subsequent generations in the absence of the RNA trigger was Met1-dependent. Maintenance of methylation associated with systemic PTGS was also found to be Met1-independent. Conclusions: RNA-triggered events can lead to heritable changes in gene expression, and it is possible that initiation of other epigenetic phenomena such as trans-silencing and paramutation may have an RNA component.", 
"In plants, the mechanism by which RNA can induce de novo cytosine methylation of homologous DNA is poorly understood. Cytosines in all sequence contexts become modified in response to RNA signals [1, 2]. Recent work has implicated the de novo DNA methyltransferases (DMTases), DRM1 and DRM2, in establishing RNA-directed methylation of the constitutive nopaline synthase promoter [3], as well as the DMTase MET1 [4] and the putative histone deacetylase HDA6 [5] in maintaining or enhancing CpG methylation induced by RNA. Despite the identification of enzymes that catalyze epigenetic modifications in response to RNA signals, it is unclear how RNA targets DNA for methylation. A screen for mutants defective in RNA-directed DNA methylation identified a novel putative chromatin-remodeling protein, DRD1. This protein belongs to a previously undefined, plant-specific subfamily of SW12/SNF2-like proteins most similar to the RAD54/ATRX subfamily. In drd1 mutants, RNA-induced non-CpG methylation is almost eliminated at a target promoter, resulting in reactivation, whereas methylation of centromeric and rDNA repeats is unaffected ' Thus, unlike the SNF2-like proteins DDM1/Lsh1 [6, 7] and ATRX [8, 9], which regulate methylation of repetitive sequences, DRD1 is not a global regulator of cytosine methylation. DRD1 is the first SNF2-like protein implicated in an RNA-guided, epigenetic modification of the genome.", 
"Methylation of cytosine residues in eukaryotic genomes is often associated with repeated sequences including transposons and their derivatives [1, 2]. Methylation has been implicated in control of two potential deleterious effects of these repeats: (1) uncontrolled transcription [2-4], which often disturbs proper expression of nearby host genes [5, 6], and (2) changes in genome structure by transposition and ectopic recombination [2, 7]. Arabidopsis thaliana provides a genetically tractable system to examine these possibilities, since viable mutants in DNA methyltransferases are available. Arabidopsis MET1 (METHYLTRANSFERASE 1, ortholog of mammalian DNA methyltransferase Dnmt1) is necessary for maintaining genomic cytosine methylation at 5'-CG-3' sites [8, 9]. Arabidopsis additionally methylates non-CG sites using CHROMO-METHYLASE3 (CMT3) [10, 11]. We examined the mobility of endogenous CACTA transposons in met1, cmt3, and cmt3-met1 mutants. High-frequency transposition of CACTA elements was detected in cmt3-met1 double mutants. Single mutants in either met1 or cmt3 were much less effective in mobilization, despite significant induction of CACTA transcript accumulation. These results lead us to conclude that CG and non-CG methylation systems redundantly function for immobilization of transposons. Non-CG methylation in plants may have evolved as an additional epigenetic tag dedicated to transposon control. This view is consistent with the recent finding that CMT3 preferentially methylates transposon-related sequences [12].", 
"Background: The genes of the trithorax (trxG) and Polycomb groups (PcG) are best known for their regulatory functions in Drosophila, where they control homeotic gene expression. Plants and animals are thought to have evolved multicellularity independently. Although homeotic genes control organ identity in both animals and plants, they are unrelated. Despite this fact, several plant homeotic genes are negatively regulated by plant genes similar to the repressors from the animal PcG. However, plant-activating regulators of the trxG have not been characterized. Results: We provide genetic, molecular, functional, and biochemical evidence that an Arabidopsis gene, ATK1, which is similar to the Drosophila trx, regulates floral organ development. The effects are specific: structurally and functionally related flower homeotic genes are under different control. We show that ATX1 is an epigenetic regulator with histone H3K4 methyltransferase activity. This is the first example of this kind of enzyme activity reported in plants, and, in contrast to the Drosophila and the yeast trithorax homologs, ATX1 can methylate in the absence of additional proteins. In its ability to methylate H3K4 as a recombinant protein, ATX1 is similar to the human homolog. Conclusions: ATX1 functions as an activator of homeotic genes, like Trithorax in animal systems. The histone methylating activity of the ATX1-SET domain argues that the molecular basis of these effects is the ability of ATX1 to modify chromatin structure. Our results suggest a conservation of trxG function between the animal and plant kingdoms despite the different structural nature of their targets.", 
"Background: Arabidopsis mutations causing genome-wide hypomethylation are viable but display a number of specific developmental abnormalities, including some that resemble known floral homeotic mutations. We previously showed that one of the developmental abnormalities present in an antisense-METHYLTRANSFERASEI (METI) transgenic line resulted from ectopic hypermethylation of the SUPERMAN gene. Results: Here, we investigate the extent to which hypermethylation of SUPERMAN occurs in several hypomethylation mutants, and describe methylation effects at a second gene, AGAMOUS. SUPERMAN gene hypermethylation occurred at a high frequency in several mutants that cause overall decreases in genomic DNA methylation. The hypermethylation pattern was largely similar in the different mutant backgrounds. Genetic analysis suggests that hypermethylation most likely arose either during meiosis or somatically in small sectors of the plant. A second floral development gene, AGAMOUS, also became hypermethylated and silenced in an Arabidopsis antisense-METI line. Conclusions: These results suggest that ectopic hypermethylation of specific genes in mutant backgrounds that show overall decreases in methylation may be a widespread phenomenon that could explain many of the developmental defects seen in Arabidopsis methylation mutants. This resembles a phenomenon seen in cancer cells, which can simultaneously show genome-wide hypomethylation and hypermethylation of specific genes. Comparison of the methylated sequences in SUPERMAN and AGAMOUS suggests that hypermethylation could involve DNA secondary structures formed by pyrimidine-rich sequences.", 
"Covalent modifications of chromatin have emerged as key determinants of the genome's transcriptional competence [1-3]. Histone H3 lysine 9(H3K9) methylation is an epigenetic signal that is recognized by HP1 [4, 5] and correlates with gene silencing in a variety of organisms [3]. Discovery of the enzymes that catalyze H3K9 methylation [6-8] has identified a second gene-specific function for this modification in transcriptional repression [9-11]. Whether H3K9 methylation is causative in the initiation and establishment of gene repression or is a byproduct of the process leading to the repressed state remains unknown. To investigate the role of HMTs and specifically H3K9 methylation in gene repression, we have employed engineered zinc-finger transcription factors (ZFPs) to target HMT activity to a specific endogenous gene. By utilizing ZFPs that recognize the promoter of the endogenous VEGF-A gene [12], and thus employing this chromosomal locus as an in vivo reporter, we show that ZFPs linked to a minimal catalytic HMT domain affect local methylation of histone H3K9 and the consequent repression of target gene expression. Furthermore, amino acid substitutions within the HMT that ablate its catalytic activity (6] effectively eliminate the ability of the UP fusions to repress transcription. Thus, H3K9 methylation is a primary signal that is sufficient for initiating a gene repression pathway in vivo.", 
"Function of the heart begins long before its formation is complete. Analyses in mouse and zebrafish have shown that myocardial function is not required for early steps of organogenesis, such as formation of the heart tube or chamber specification. However, whether myocardial function is required for later steps of cardiac development, such as endocardial cushion (EC) formation, has not been established. Recent technical advances and approaches have provided novel inroads toward the study of organogenesis, allowing us to examine the effects of both genetic and pharmacological perturbations of myocardial function on EC formation in zebrafish. To address whether myocardial function is required for EC formation, we examined silent heart (sih(-/-)) embryos, which lack a heartbeat due to mutation of cardiac troponin T (tnnt2), and observed that atrioventricular (AV) ECs do not form. Likewise, we determined that cushion formation is blocked in cardiofunk (cfk(-/-)) embryos, which exhibit cardiac dilation and no early blood flow. In order to further analyze the heart defects in cfk(-/-) embryos, we positionally cloned cfk and show that it encodes a novel sarcomeric actin expressed in the embryonic myocardium. The Cfk(s11) variant exhibits a change in a universally conserved residue (R177H). We show that in yeast this mutation negatively affects actin polymerization. Because the lack of cushion formation in sih- and cfk-mutant embryos could be due to reduced myocardial function and/or lack of blood flow, we approached this question pharmacologically and provide evidence that reduction in myocardial function is primarily responsible for the defect in cushion development. Our data demonstrate that early myocardial function is required for later steps of organogenesis and suggest that myocardial function, not endothelial shear stress, is the major epigenetic factor controlling late heart development. Based on these observations, we postulate that defects in cardiac morphogenesis may be secondary to mutations affecting early myocardial function, and that, in humans, mutations affecting embryonic myocardial function may be responsible for structural congenital heart disease.", 
"Many proteins can misfold into beta-sheet-rich, self-seeding polymers (amyloids). Prions are exceptional among such aggregates in that they are also infectious. In fungi, prions are not pathogenic but rather act as epigenetic regulators of cell physiology, providing a powerful model for studying the mechanism of prion replication. We used prion-forming domains from two budding yeast proteins (Sup35p and New1p) to examine the requirements for prion formation and inheritance. In both proteins, a glutamine/asparagine-rich (Q/N-rich) tract mediates sequence-specific aggregation, while an adjacent motif, the oligopeptide repeat, is required for the replication and stable inheritance of these aggregates. Our findings help to explain why although Q/N-rich proteins are relatively common, few form heritable aggregates: prion inheritance requires both an aggregation sequence responsible for self-seeded growth and an element that permits chaperone-dependent replication of the aggregate. Using this knowledge, we have designed novel artificial prions by fusing the replication element of Sup35p to aggregation-prone sequences from other proteins, including pathogenically expanded polyglutamine.", 
"In contrast to the biallelic expression of most genes, expression of genes subject to genomic imprinting is monoallelic and based on the sex of the transmitting parent. Possession of only a single active allele can lead to deleterious health consequences in humans. Aberrant expression of imprinted genes, through either genetic or epigenetic alterations, can result in,developmental failures, neurodevelopmental and neurobehavioral disorders and cancer. The evolutionary emergence of imprinting occurred in a common ancestor to viviparous mammals after divergence from the egg-laying monotremes. Current evidence indicates that imprinting regulation in metatherian mammals differs from that in eutherian mammals. This suggests that imprinting mechanisms are evolving from those that were established 150 million years ago. Therefore, comparing genomic sequence of imprinted domains from marsupials and eutherians with those of orthologous regions in monotremes offers a potentially powerful bioinformatics approach for identifying novel imprinted genes and their regulatory elements. Such comparative studies will also further our understanding of the molecular evolution and phylogenetic distribution of imprinted genes. BioEssays25:577-588,2003. (C) 2003 Wiley Periodicals, Inc.", 
"In female mammals, a single X chromosome is stably and heritably silenced early in embryogenesis [1]. The inactive X is characterized by asynchronous DNA replication [2, 3] and epigenetic chromatin modifications, including DNA methylation [4], histone H3/H4 hypoacetylation [5-7], and incorporation of a variant histone macroH2A [8-10]. X inactivation is initiated by a cis-acting RNA molecule, the X-inactive specific transcript (Xist), which coats the chromosome (11-17]. However, the mechanism by which Xist induces chromosome silencing is poorly understood. An important approach towards answering this question has been to determine the temporal order of epigenetic chromatin modifications in an in vitro model system, differentiating XX embryonic stem (ES) cells, and thereby to identify candidate targets for Xist RNA [18-21]. To date, these studies have demonstrated that, following accumulation of Xist RNA [18, 20], the transition to late replication of the X chromosome is the earliest detectable event [19]. H4 hypoacetylation [19], macroH2A1.2 incorporation [21], and DNA methylation [19] all occur subsequently. Recently, it has been shown that chromatin of the inactive X is also characterized by methylation of histone H3 at lysine 9 (H3-K9) [22, 23]. Here we show that H3-K9 methylation is a very early event in the process of X inactivation, which closely parallels the onset of Xist RNA accumulation.", 
"The information contained within the linear sequence of bases (the genome) must be faithfully replicated in each cell cycle, with a balance of constancy and variation taking place over the course of evolution. Recently, it has become clear that additional information important for genetic regulation is contained within the chromatin proteins associated with DNA (the epigenome). Epigenetic information also must be faithfully duplicated in each cell cycle, with a balance of constancy and variation taking place during the course of development to achieve differentiation while maintaining identity within cell lineages. Both the genome and the epigenome are synthesized at the replication fork, so the events occurring during S-phase provide a critical window of opportunity for eliciting change or maintaining existing epigenetic states. Cells discriminate between different states of chromatin through the activities of proteins that selectively modify the structure of chromatin. Several recent studies report the localization of certain chromatin-modifying proteins to replication forks at specific times during S-phase. Since transcriptionally active and inactive chromosome domains generally replicate at different times during S-phase, this spatiotemporal regulation of chromatin assembly proteins may be an integral part of epigenetic inheritance. (C) 2003 Wiley Periodicals, Inc.", 
"DNA methylation has been implicated in a variety of epigenetic processes, and abnormal methylation patterns have been seen in tumors [1-3]. Analysis of methylation patterns has traditionally been conducted either by using Southern analysis after cleavage with methyl-sensitive restriction endonucleases or by bisulfite sequencing [4]. However, neither method is practical for analyzing more than a few genes. Here, we describe a simple technique for genome-wide mapping of DNA methylation patterns. Fragmentation by a methyl-sensitive restriction endonuclease is followed by size fractionation and hybridization to microarrays. We demonstrate the utility of this method by characterizing methylation patterns in Arabidopsis methylation mutants. This analysis reveals that CHROMOMETHYLASE3 (CMT3) [5], which was previously shown to maintain CpXpG methylation [6,7], preferentially methylates transposons, even when they are present as single copies within the genome. Methylation profiling has potential applications in disease research and diagnostic screening.", 
"Nutritional regulatory responses were compared for the cryptic 'solitarious' and the conspicuously coloured, aggregating 'gregarious' phases of the desert locust Schistocerca gregaria. The desert locust has the genetic potential to exist in either phase, changing between them within a lifetime and epigenetically across generations. Our aim was to compare final-instar nymphs of the two phases with respect to key nutritional variables, including (i) points of regulated intake (the 'intake target') for protein and carbohydrate, (ii) the nature of trade-offs between over-eating nutrients in excess and under-eating those in deficit when fed nutritionally unbalanced foods, (iii) diet-related patterns of nutrient utilisation, and (iv) the performance consequences of eating nutritionally unbalanced diets. When provided with pairs of nutritionally unbalanced but complementary foods, both phases regulated their intake of protein and carbohydrate to a similar point. However, when confined to foods that were of unbalanced protein to carbohydrate ratio, gregarious nymphs ate more than solitarious insects. Both phases regulated protein growth, but gregarious insects did so to a lower adult body protein content and converted ingested protein to growth less efficiently. When fed a food high in carbohydrate and low in protein, gregarious nymphs deposited more body lipid and survived less well than did solitarious insects. Solitarious nymphs developed more quickly than gregarious nymphs except on the two most extremely unbalanced diets, on which development time was similar. The results are discussed with respect to the different nutritional ecologies of the two phases and used to develop the hypothesis that animals have evolved to trade-off the cost of eating excess of a nutritionally unbalanced diet against the probability of encountering foods of complementary composition in the future.", 
"Whether exposure to radiation emitted from cellular phones poses a health hazard is at the focus of current debate. We have examined whether in vitro exposure of human peripheral blood lymphocytes (PBL) to continuous 830 MHz electromagnetic fields causes losses and gains of chromosomes (aneuploidy), a major somatic mutation leading to genomic instability and thereby to cancer. PBL were irradiated at different average absorption rates (SAR) in the range of 1.6-8.8 W/kg for 72 hr in an exposure system based on a parallel plate resonator at temperatures ranging from 34.5-37.5 degreesC. The averaged SAR and its distribution in the exposed tissue culture flask were determined by combining measurements and numerical analysis based on a finite element simulation code. A linear increase in chromosome 17 aneuploidy was observed as a function of the SAR value, demonstrating that this radiation has a genotoxic effect. The SAR dependent aneuploidy was accompanied by an abnormal mode of replication of the chromosome 17 region engaged in segregation (repetitive DNA arrays associated with the centromere), suggesting that epigenetic alterations are involved in the SAR dependent genetic toxicity. Control experiments (i.e., without any RF radiation) carried out in the temperature range of 34.5-38.5 degreesC showed that elevated temperature is not associated with either the genetic or epigenetic alterations observed following RF radiation-the increased levels of aneuploidy and the modification in replication of the centromeric DNA arrays. These findings indicate that the genotoxic effect of the electromagnetic radiation is elicited via a non-thermal pathway. Moreover, the fact that aneuploidy is a phenomenon known to increase the risk for cancer, should be taken into consideration in future evaluation of exposure guidelines. (C) 2003 Wiley-Liss. Inc.", 
"One of the enigmas in tumor biology is that different types of cancers are prevalent in different age groups. One possible explanation is that the ability of a specific oncogene to cause tumorigenesis in a particular cell type depends on epigenetic parameters such as the developmental context. To address this hypothesis, we have used the tetracycline regulatory system to generate transgenic mice in which the expression of a c-MYC human transgene can be conditionally regulated in murine hepatocytes. MYC's ability to induce tumorigenesis was dependent upon developmental context. In embryonic and neonatal mice, MYC overexpression in the liver induced marked cell proliferation and immediate onset of neoplasia. In contrast, in adult mice MYC overexpression induced cell growth and DNA replication without mitotic cell division, and mice succumbed to neoplasia only after a prolonged latency. In adult hepatocytes, MYC activation failed to induce cell division, which was at least in part mediated through the activation of p53. Surprisingly, apoptosis is not a barrier to MYC inducing tumorigenesis. The ability of oncogenes to induce tumorigenesis may be generally restrained by developmentally specific mechanisms. Adult somatic cells have evolved mechanisms to prevent individual oncogenes from initiating cellular growth, DNA replication, and mitotic cellular division alone, thereby preventing any single genetic event from inducing tumorigenesis.", 
"We investigated the. randomness and uniqueness of human iris patterns by mathematically comparing 2.3 million different pairs of eve images. The phase structure of each iris pattern was extracted by demodulation with quadrature wavelets spanning several scales of analysis. The resulting distribution of phase sequence variation anion different eyes was precisely binomial, revealing 244 independent degrees of freedom. This amount of statistical variability corresponds to an entropy (information density) of about 3.2 bits mm(-2) over the iris. It implies that the probability of two different irides agreeing by chance in more than 70% of their phase sequence is about one in 7 billion. We also compared images of genetically identical irides, from the left and right eyes of 324 persons, and from monozygotic twins. Their relative phase sequence variation generated the same statistical distribution as did unrelated eyes. This indicates that apart from overall form and colour. iris patterns are determined epigenetically by random events in the morphogenesis of this tissue. The resulting diversity, and the combinatorial complexity created by so many dimensions of random variation, mean that the failure of a simple test of statistical independence performed on iris patterns can serve as a reliable rapid basis for automatic personal identification.", 
"The C. elegans proteins MES-2 and MES-6, orthologs of the Polycomb group (PcG) chromatin repressors E(Z) and ESC [1, 2], exist in a complex with their novel partner MES-3 [3]. The MES system participates in silencing the X chromosomes in the hermaphrodite germline [4, 5]. Loss of maternal MES function leads to germline degeneration and sterility [6]. We report here that the MES complex is responsible for di- and trimethylation of histone H3 Lys27 (H3-K27) in the adult germline and in early embryos and that MES-dependent H3-K27 marks are concentrated on the X's. Another H3-K27 HMT functions in adult somatic cells oocytes, and the PGCs of embryos. In PGCs, the ME; complex may specifically convert dimethyl to trimethyl H3-K27. The HMT activity of the MES complex appears to be dependent on the SET domain of MES-2. MES-2 thus joins its orthologs Drosophila E(Z) and human EZH2 among SET domain proteins known to function as HMTs (reviewed in [7]). Methylation of histones is important for long-term epigenetic regulation of chromatin and plays a key role in diverse processes such as X inactivation and oncogenesis [8]. Our results contribute to understanding the composition and roles of E(Z)/MES-2 complexes across species.", 
"Remodeling of microvascular networks in mammals is critical for physiological adaptations and therapeutic revascularization. Cellular behaviors such as proliferation, differentiation, and migration are coordinated in these remodeling events via combinations of biochemical and biomechanical signals. We developed a cellular automata (CA) computational simulation that integrates epigenetic stimuli, molecular signals, and cellular behaviors to predict microvascular network patterning events. Over 50 rules obtained from published experimental data govern independent behaviors (including proliferation, differentiation, and migration) of thousands of interacting cells and diffusible growth factors in their tissue environment. From initial network patterns of in vivo blood vessel networks, the model predicts emergent patterning responses to two stimuli: 1) network-wide changes in hemodynamic mechanical stresses, and 2) exogenous focal delivery of an angiogenic growth factor. The CA model predicts comparable increases in vascular density (370 +/- 29 mm/mm(3)) 14 days after treatment with exogenous growth factor to that in vivo (480 +/- 41 mm/mm(3)) and approximately a twofold increase in contractile vessel lengths 5-10 days after 10% increase in circumferential wall strain, consistent with in vivo results. The CA simulation was thus able to identify a functional patterning module capable of quantitatively predicting vessel network remodeling in response to two important epigenetic stimuli.", 
" ", 
"Allopolyploidy, the joining of two parental genomes in a polyploid organism with diploid meiosis, is an important mechanism of reticulate evolution. While many successful long-established allopolyploids are known, those formed recently undergo an instability phase whose basis is now being characterized. We describe observations made with the Arabidopsis system that include phenotypic instability, gene silencing and activation, and methylation changes. We present a model based on the epigenetic destabilization of genomic repeats, which in the parents are heterochromatinized and suppressed. We hypothesize that loss of epigenetic suppression of these sequences, here defined as the heterome, results in genomic instability including silencing of single-copy genes.", 
" ", 
"Reproductive isolation is considered to play a key part in evolution, and plants and animals have developed a range of strategies that minimize gene flow between species. In plants, these strategies involve either pre-zygotic barriers, such as differences in floral structure and pollen-stigma recognition, or post-zygotic barriers, which are less well understood and affect aspects of seed development ranging from fertilization to maturation. In most angiosperms, a double fertilization event gives rise to a zygote and the endosperm: a triploid tissue with an unequal parental genomic contribution, which, like the placenta of mammals, provides reserves to the developing embryo. Interestingly, many aspects of endosperm development, again like the placenta, are regulated by a range of epigenetic mechanisms that are globally termed imprinting. Imprinted genes are characterized by their uniparental expression, the other parental allele being silenced. Normal development of the endosperm thus requires a highly specific balance of gene expression, from either the maternal or paternal genomes. Any alteration of this balance resulting from changes in allelic copy number, sequence or epigenetic imprints can cause endosperm failure and eventual seed abortion. In its widest sense, the endosperm thus serves as an accurate 'sensor' of compatibility between parents. A first step in understanding this important, yet complex system must clearly be the isolation and characterization of as wide a range as possible of imprinted genes.", 
"Embryonic stem (ES) cells are permanent pluripotent stem cell lines established from pre-implantation mouse embryos. There is currently great interest in the potential therapeutic applications of analogous cells derived from human embryos. The isolation of ES cells is commonly presented as a straightforward transfer of cells in the early embryo into culture. In reality, however, continuous expansion of pluripotent cells does not occur in vivo, and in vitro is the exception rather than the norm. Both genetic and epigenetic factors influence the ability to derive ES cells. We have tracked the expression of a key marker and determinant of pluripotency, the transcription factor Oct-4, in primary cultures of mouse epiblasts and used this to assay the effect of experimental manipulations on the maintenance of a pluripotent cell compartment. We find that expression of Oct-4 is often lost prior to overt cytodifferentiation of the epiblast. The rate and extent of Oct-4 extinction varies with genetic background. We report that treatment with the MAP kinase/ERK kinase inhibitor PD98059, which suppresses activation of the mitogen-activated protein kinases Erk1 and Erk2, results in increased persistence of Oct-4-expressing cells. Oct-4 expression is also relatively sustained in cultures of diapause embryos and of isolated inner cell masses. Combination of all three conditions allowed the derivation of germline-competent ES cells from the normally refractory CBA mouse strain. These findings suggest that the genesis of an ES cell is a relatively complex process requiring epigenetic modulation of key gene expression over a brief time-window. Procedures that extend this time-window and/or directly regulate the critical genes should increase the efficiency of ES cell derivation.", 
"We suggest simulating evolution of complex organisms using a model constrained solely hv the requirement of robustness in its expression patterns. This scenario is illustrated by evolving discrete logical networks with epigenetic properties. Evidence for dynamical features in the evolved networks is found that carl be related to biological observables.", 
"Purpose: To investigate the associations between inflammation tests and radiation dose in A-bomb survivors. Subjects and methods: Subjects were A-bomb survivors who underwent inflammation tests of leukocyte counts, neutrophil counts, erythrocyte sedimentation rate, corrected erythrocyte sedimentation rate, alpha -1 globulin, alpha -2 globulin and sialic acid between 1988 and 1992. Associations with radiation dose (DS86) were analyzed by regression analysis and heterogeneity among inflammatory diseases, anaemia at examination, or history of cancer was also tested. Results: The associations with radiation dose were statistically significant for leukocyte counts (71.0 mm(-3) Gy(-1), p=0.015), erythrocyte sedimentation rate (1.58 mm h(-1) Gy(-1), p=0.0001), corrected erythrocyte sedimentation rate (1.14 mm h(-1) Gy(-1), p=0.0001), alpha -1 globulin (0.0057 g dl(-1) Gy(-1), p=0.0001), alpha -2 globulin (0.0128 g dl(-1) Gy(-1), p=0.0001), and sialic acid (1.2711 mg dl(-1) Gy(-1), p = 0.0001) but not for neutrophil counts (29.9 mm(-3) Gy(-1), p=0.17). Heterogeneity was not statistically significant. Among inflammatory diseases, associations were the strongest for chronic thyroiditis and chronic liver diseases. Conclusions: This study suggests statistically significant association between inflammation in A-bomb survivors and radiation dose of during 1988-1992. The association might contribute, as an epigenetic and/or bystander effect, to development of several radiation-induced disorders.", 
"Epigenetic asymmetry between parental genomes and embryonic lineages exists at the earliest stages of mammalian development. The maternal genome in the zygote is highly methylated in both its DNA and its histones and most imprinted genes have maternal germline methylation imprints. The paternal genome is rapidly remodelled with protamine removal, addition of acetylated histories, and rapid demethylation of DNA before replication. A minority of imprinted genes have paternal germline methylation imprints. Methylation and chromatin reprogramming continues during cleavage divisions, but at the blastocyst stage lineage commitment to inner cell mass (ICM) or trophectoderm (TE) fate is accompanied by a dramatic increase in DNA and histone methylation, predominantly in the ICM. This may set up major epigenetic differences between embryonic and extraembryonic tissues, including in X-chromosome inactivation and perhaps imprinting. Maintaining epigenetic asymmetry appears important for development as asymmetry is lost in cloned embryos, most of which have developmental defects, and in particular an imbalance between extraembryonic and embryonic tissue development.", 
"The polymerization of many amyloids is a two-stage process initiated by the formation of a seeding nucleus or protofibril. Soluble protein then assembles with these nuclei to form amyloid fibers. Whether fiber growth is bidirectional or unidirectional has been determined for two amyloids, In these cases, bidirectional growth was established by time lapse atomic-force microscopy, Here, we investigated the growth of amyloid fibers formed by NM, the prion-determining region of the yeast protein Sup35p, The conformational changes in NM that lead to amyloid formation in vitro serve as a model for the self-perpetuating conformational changes in Sup35p that allow this protein to serve as an epigenetic element of inheritance in vivo. To assess the directionality of fiber growth, we genetically engineered a mutant of NM so that it contained an accessible cysteine residue that was easily labeled after fiber formation. The mutant protein assembled in vitro with kinetics indistinguishable from those of the wild-type protein and propagated the heritable genetic trait [PSI+] with the same fidelity. In reactions nucleated with prelabeled fibers, unlabeled protein assembled at both ends. Thus, NM fiber growth is bidirectional. (C) 2001 Elsevier Science Ltd. All rights reserved.", 
"Background: Members of the GATA family of zinc finger transcription factors are genetically controlled master regulators of development in the hematopoietic and nervous systems. Whether GATA factors also serve to integrate epigenetic signals on target promoters is, however, unknown. The transforming growth factor-beta (TGF-beta) superfamily is a large group of phylogenetically conserved secreted factors controlling cell proliferation, differentiation, migration, and survival in multiple tissues. Results: GATA-3, a key regulator of T helper cell development, was found to directly interact with Smad3, an intracellular signal transducer of TGF-beta. Complex formation required a central region in GATA-3 and the N-terminal domain of Smad3. GATA-3 mediated recruitment of Smad3 to GATA binding sites independently of Smad3 binding to DNA, and the two factors cooperated synergistically to regulate transcription from the IL-5 promoter in a TGF-beta-dependent manner. Treatment of T helper cells with TGF-beta promoted the formation of an endogenous Smad3/GATA-3 nuclear complex and stimulated production of the Th2 cytokine IL-10 in a Smad3- and GATA-3-dependent manner. Conclusions: Although Smad proteins are known to interact with a number of general transcription factors, these are insufficient to explain the tissue-specific biology of TGF-beta proteins. Through its interaction with Smad3, GATA-3 is able to integrate a genetic program of cell differentiation with an extracellular signal, providing a molecular framework for the effects of TGF-beta on the development and function of specific subsets of immune cells and possibly other cell types.", 
"Whenever the state of a biological system is not determined solely by present conditions but depends on its past history, we can say that the system has memory. Bacteria and bacteriophage use a variety of memory mechanisms, some of which seem to convey adaptive value. A genetic type of heritable memory is the programmed inversion of specific DNA sequences, which causes switching between alternative patterns of gene expression. Heritable memory can also be based on epigenetic circuits, in which a system with two possible steady states is locked in one or the other state by a positive feedback loop. Epigenetic states have been observed in a variety of cellular processes, and are maintained by diverse mechanisms. Some of these involve alternative DNA methylation patterns that are stably transmitted to daughter molecules and can affect DNA-protein interactions (e.g., gene transcription). Other mechanisms exploit autocatalytic loops whereby proteins establish the proper conditions for their continued synthesis. Template polymers other than nucleic acids (e.g., components of the cell wall) may also propagate epigenetic states. Non-heritable memory is exemplified by parasitic organisms that bear a signature of their previous host, such as host-controlled modification of phage DNA or porin hitchhiking in predatory bacteria. The heterogeneous nature of the examples known may be indicative of widespread occurrence of memory mechanisms in bacteria and phage. However, the actual extent, variety and potential selective value of prokaryotic memory devices remain open questions, still to be addressed experimentally. (C) 2002 Wiley Periodicals, Inc.", 
"Recent inquiries have revealed a surprisingly large number (>2500) of naturally occurring antisense transcripts [1-4], but their function remains largely undiscovered. A better understanding of antisense mechanisms is clearly needed because of their potentially diverse roles in gene regulation and disease [5-8]. A well-documented case occurs in X inactivation, the mechanism by which X-linked gene expression is equalized between XX females and XY males [9]. The antisense gene Tsix [6] determines X chromosome choice and represses the noncoding silencer, Xist [10-12]. In principle, Tsix action may involve RNA, the act of transcription, or local chromatin. Here, we create novel Tsix alleles to distinguish transcription-versus RNA-based mechanisms. When Tsix transcription is terminated before Xist (Tsix(TRAP)), Tsix cannot block Xist upregulation, suggesting the importance of overlapping antisense transcription. To separate the act of transcription from RNA, we knocked in Tsix cDNA in the reverse orientation (Tsix(cDNA)) to restore RNA levels in cis without concurrent transcription across Xist. However, Tsix(cDNA) cannot complement Tsix(TRAP). Surprisingly, both mutations disrupt choice, indicating that this epigenetic step requires transcription. We conclude that the processed antisense RNA does not act alone and that Tsix function specifically requires antiparallel transcription through Xist. A mechanism of transcription-based feedback regulation is proposed.", 
"Malignant brain tumors consist of a number of distinct subclonal populations. Each of these subpopulations may be characterized by its own behaviors and properties. These subpopulations arise from the constant genetic and epigenetic alteration of existing cells in the rapidly growing tumor. However, since each single-cell mutation only leads to a small number of offspring initially, very few newly arisen subpopulations survive more than a short time. The present work quantifies emergence, i.e, the likelihood of an isolated subpopulation surviving for an extended period of time. Only competition between clones is considered; there are no cooperative effects included. The probability that a subpopulation emerges under these conditions is found to be a sigmoidal function of the degree of change in cell division rates. This function has a non-zero value for mutations which confer no advantage in growth rate, which represents the emergence of a distinct subpopulation with an advantage that has yet to be selected for, such as hypoxia tolerance or treatment resistance. A logarithmic dependence on the size of the mutated population is also observed. A significant probability of emergence is observed for subpopulations with any growth advantage that comprise even 0.1% of the proliferative cells in a tumor. The impact of even two clonal populations within a tumor is shown to be sufficient such that a prognosis based on the assumption of a monoclonal tumor can be markedly inaccurate. (C) 2000 Academic Press.", 
"Controversy has reigned for some time over the biological connection between DNA methylation and cancer. For this reason, the methylation mechanism responsible for increased cancer risk has received greater attention in recent years. Tumor suppressor genes are often hyper-methylated resulting in gene silencing. Although some have questioned this interpretation of the link between methylation and cancer, it appears that both hyper-methylation and hypomethylation events can create epigenetic changes that can contribute to cancer development. Recent studies have shown that the methyltransferases DNMT1 and DNMT3b cooperatively maintain DNA methylation and gene silencing in human cancer cells. Disruption of the human DNMT3b only slightly reduces the overall global DNA methylation; however, demethylation was markedly potentiated when both DNMT1 and DNMT3b were simultaneously deleted. The results to these experiments provide compelling evidence towards a role for DNA methylation in cancer. This review discusses the current understanding of cancer-epigenetic information and highlights recent studies that connect the methylation machinery and chromatin remodelling with cancer susceptibility. (C) 2003 Wiley Periodicals, Inc.", 
"The transplacental exposure of fetuses to maternal cigarette smoke may increase the risk of developmental impairments, congenital diseases, and childhood cancer. The whole-body exposure of Swiss mice to environmental cigarette smoke (ECS) during pregnancy decreased the number of fetuses per dam, placenta weight, and fetus weight. ECS increased DNA adducts, oxidative nucleotide alterations, and cytogenetic damage in fetus liver. Evaluation by cDNA array of 746 genes showed that 61 of them were expressed in fetus liver under basal conditions. The oral administration of N-acetylcysteine (NAC) during pregnancy enhanced the expression of three genes only, including two glutathione S-transferases and alpha1-antitrypsin precursor, whose deficiency plays a pathogenetic role in congenital emphysema. Transplacental ECS upregulated the expression of 116 genes involved in metabolism, response to oxidative stress, DNA and protein repair, and signal transduction. NAC inhibited the ECS-related genetic damage and upregulation of most genes. ECS stimulated pro-apoptotic genes and genes downregulating the cell cycle, which may justify growth impairments in the developing fetus. Thus, both genetic and epigenetic mechanisms were modulated by ECS. Moreover, hypoxia-related genes and several oncogenes and receptors involved in proliferation and differentiation of leukocytes were induced in the fetal liver, which also bears hematopoietic functions.", 
" ", 
"The purpose of the present study was to investigate the effect of thermal conditioning, (through exposure to heat stress), during pre-hatch development on some physiological responses of post-hatch broilers to a post-natal heat stress challenge. Exposure to heat stress at this stage, we hope, may possibly induce epigenetic heat adaptation. Incubating eggs were exposed to temperature of 39.0degreesC for 2 h from Day 13 to 17 of incubation. At 33, 35, 37, 39, 41 and 43 d of age, the broilers hatched from these eggs were housed individually in open-circuit respiration cells. The climatic chambers were set to 22degreesC and increased to 30degreesC for 4 h. O-2 consumption and CO2 production of each chicken was monitored continuously in order to calculate the heat production. Blood samples were obtained before and during the 4 h heat stress. Thermal conditioning during incubation did not affect the plasma T-4, corticosterone, glucose, uric acid and CK concentrations. Temperature challenge, decreased plasma T-3 of broilers of both groups but the decrease was greater in pre-conditioned broilers compared with controls. A similar trend was observed for triglycerides. These changes did not affect total heat production. Since decreased T3 and triglyceride levels are part of the mechanisms for thermoregulation, these suggest that thermal conditioning during incubation can improve the broiler chicken capability for thermotolerance at later post-hatch age. (C) 2002 Elsevier Science Ltd. All rights reserved.", 
"Autosomal genes that are subject to random allelic Inactivation (RAI), like imprinted genes [1] and genes subject to X-inactivation Gal, require mechanisms that dictate the differential transcriptional regulation of two sequence-identical alleles. RAI genes include olfactory receptor genes [3], and the various genes encoding antigen receptors on lymphocytes (immunoglobulin genes, T cell receptor genes and NK receptor genes [4-7]). These observations raise the possibility that other genes might be similarly regulated. Moreover, an interesting possibility is that certain genes might be monoallelically expressed in some cells and biallelically expressed in others. Recently, reports of monoallelic expression of interleukin-2 (IL-2) [8,9] and IL-4 [10,11] have raised the possibility that the cytokine gene family may be subject to monoallelic expression. Another report suggests that the gene encoding the transcription factor Pax-5, which is involved in B-cell (and cerebellar) development [12,13], is also subject to monoallelic expression [14]. Using a novel single-cell reverse transcription-polymerase chain reaction (RT PCR) approach, we have analyzed the IL-2 and Pax-5 genes in mice. We found that IL-2 is monoallelically transcribed in some T cells and biallelically transcribed in others, raising interesting questions regarding cytokine gene regulation. Additionally, our analyses suggest that Pax-5 is consistently biallelically transcribed. Thus, the IL-2 gene and other cytokine genes may be regulated in a stochastic manner that results in 0, 1 or 2 alleles of a given cytokine gene expressed in each T cell. This type of regulation could account for the wide variety of different combinations of cytokine genes expressed in individual T cells and therefore plays a role in the generation of T cells with a range of different effector functions. (C) 2000 Elsevier Science Ltd. All rights reserved.", 
"Recent studies on the transcriptional regulation of two linked, imprinted genes, Igf2 and H19, have provided evidence for a novel mechanism of epigenetic control. DNA methylation controls the activity of an insulator element located between the two linked genes by regulating the binding of the zinc-finger protein CTCF. (C) 2000 Elsevier Science Ltd. All rights reserved.", 
"Reversible acetylation of histone tails plays an important role in chromatin remodelling and regulation of gene activity [1, 2]. While modification by histone acetyltransferase (HAT) is usually linked to transcriptional activation, we provide here evidence for HAT function in several types of epigenetic repression. Chameau (Chm), a new Drosophila member of the MYST HAT family, dominantly suppresses position effect variegation (PEV), is required for the maintenance of Hox gene silencing by Polycomb group (PcG) proteins, and can partially substitute for the MYST Sas2 HAT in yeast telomeric position effect (TPE). Finally, we provide in vivo evidence that the acetyltransferase activity of Chm is required in these processes, since a variant protein mutated in the catalytic domain no longer rescues PEV modification, telomeric silencing of SAS2-deficient yeast cells, nor lethality of chm mutant flies. These findings emphasize the role of an acetyltransferase in gene silencing, which supports, according to the histone code hypothesis [2-4], that transcription at a particular locus is determined by a precise combination of histone tail modifications rather than by overall acetylation levels.", 
"Many scientists and philosophers of science are troubled by the relative isolation of developmental from evolutionary biology. Reconciling the science of development with the science of heredity preoccupied a minority of biologists for much of the twentieth century, but these efforts were not corporately successful. Mainly in the past fifteen years, however, these previously dispersed integrating programmes have been themselves synthesized and so reinvigorated. Two of these more recent synthesizing endeavours are evolutionary developmental biology (EDB, or evo-devo) and developmental systems theory (DST). While the former is a bourgeoning and scientifically well-respected biological discipline, the same cannot be said of DST, which is virtually unknown among biologists. In this review, we provide overviews of DST and EDB, summarize their key tenets, examine how they relate to one another and to the study of epigenetics, and survey the impact that DST and EDB have had (and in future should have) on biological theory and practice. (C) 2001 John Wiley & Sons, Inc.", 
"Background: SIR2 was originally identified in S. cerevisiae for its role in epigenetic silencing through the creation of specialized chromatin domains. It is the most evolutionarily conserved protein deacetylase, with homologs in all kingdoms. SIR2 orthologs in multicellular eukaryotes have been implicated in lifespan determination and regulation of the activities of transcription factors and other proteins. Although SIR2 has not been widely implicated in epigenetic silencing outside yeast, Drosophila SIR2 mutations were recently shown to perturb position effect variegation, suggesting that the role of SIR2 in epigenetic silencing may not be restricted to yeast. Results: Evidence is presented that Drosophila SIR2 is also involved in epigenetic silencing by the Polycomb group proteins. Sir2 mutations enhance the phenotypes of Polycomb group mutants and disrupt silencing of a mini-white reporter transgene mediated by a Polycomb response element. Consistent with this, SIR2 is physically associated with components of an E(Z) histone methyltransferase complex. SIR2 binds to many euchromatic sites on polytene chromosomes and colocalizes with E(Z) at most sites. Conclusions: SIR2 is involved in the epigenetic inheritance of silent chromatin states mediated by the Drosophila Polycomb group proteins and is physically associated with a complex containing the E(Z) histone methyltransferase.", 
"'Viable yellow' (A(vy)/alpha) mice are larger, obese, hyperinsulinemic, more susceptible to cancer, and, on average, shorter lived than their non-yellow siblings. They are epigenetic mosaics ranging from a yellow phenotype with maximum ectopic agouti overexpression, through a continuum of mottled agouti/yellow phenotypes with partial agouti overexpression, to a pseudoagouti phenotype with minimal ectopic expression. Pseudoagouti A(vy)/a mice are lean, healthy, and longer lived than their yellow siblings. Here we report that feeding pregnant black a/a dams methyl-supplemented diets alters epigenetic regulation of agouti expression in their offspring, as indicated by increased agouti/black mottling in the direction of the pseudoagouti phenotype, We also present confirmatory evidence that epigenetic phenotypes are maternally heritable. Thus A(vy) expression, already known to be modulated by imprinting, strain-specific modification, and maternal epigenetic inheritance, is also modulated by maternal diet. These observations suggest, at least in this special case, that maternal dietary supplementation may positively affect health and longevity of the offspring, Therefore, this experimental system should be useful for identifying maternal factors that modulate epigenetic mechanisms, especially DNA methylation, in developing embryos.", 
"Persistence of individual differences in animal behavior in reactions to various environmental challenges could reflect basic divergences in temperament, which might be used to predict details of adaptive response. Although studies have been carried out on fear and anxiety in various species, including laboratory, domestic and wild animals, no consistent definition of fearfulness as a basic trait of temperament has emerged. After a classification of the events that may produce a state of fear, this article describes the great variability in behavior and in physiological patterns generally associated with emotional reactivity. The difficulties of proposing fearfulness - the general capacity to react to a variety of potentially threatening situations - as a valid basic internal variable are then discussed. Although there are many studies showing covariation among the psychobiological responses to different environmental challenges, other studies find no such correlations and raise doubts about the interpretation of fearfulness as a basic personality trait. After a critical assessment of methodologies used in fear and anxiety studies, it is suggested that discrepancies among results are mainly due to the modulation of emotional responses in animals, which depend on numerous genetic and epigenetic factors. It is difficult to compare results obtained by different methods from animals reared under various conditions and with different genetic origins. The concept of fearfulness as an inner trait is best supported by two kinds of investigations. First, an experimental approach combining ethology and experimental psychology produces undeniable indicators of emotional reactivity. Second, genetic lines selected for psychobiological traits prove useful in establishing relationships between behavioral and neuroendocrine aspects of emotional reactivity. It is suggested that fearfulness could be considered a basic feature of the temperament of each individual, one that predisposes it to respond similarly to a variety of potentially alarming challenges, but is nevertheless continually modulated during development by the interaction of genetic traits of reactivity with environmental factors, particularly in the juvenile period. Such interaction may explain much of the interindividual variability observed in adaptive responses.", 
"Genomic instability is characterized by the increased rate of acquisition of alterations in the mammalian genome. These changes encompass a diverse set of biological end points including karyotypic abnormalities, gene mutation and amplification, cellular transformation, clonal heterogeneity and delayed reproductive cell death, The loss of stability of the genome is becoming accepted as one of the most important aspects of carcinogenesis, and the numerous genetic changes associated with the cancer cell implicate genomic stability as contributing to the neoplastic phenotype, Multiple metabolic pathways govern the accurate duplication and distribution of DNA to progeny cells; other pathways maintain the integrity of the information encoded by DNA and regulate the expression of genes during growth and development. For each of these functions, there is a normal baseline frequency at which errors occur, leading to spontaneous mutations and other genomic anomalies. This review summarizes the current status of knowledge about radiation-induced genomic instability. Those events and processes likely to be involved in the initiation and perpetuation of the unstable phenotype, the potential role of epigenetic factors in influencing the onset of genomic instability, and the delayed effects of cellular exposure to ionizing radiation are discussed. (C) 1996 by Radiation Research Society", 
"The trilaminar kinetochore directs the segregation of chromosomes in mitosis and meiosis. Despite its importance, the molecular architecture of this structure remains poorly understood [1]. The best known component of the kinetochore plates is CENP-C, a protein that is required for kinetochore assembly [2], but whose molecular role in kinetochore structure and function is unknown. Here we have raised for the first time monospecific antisera to CENP-A [3], a 17 kD centromere-specific histone variant that is 62% identical to the carboxy-terminal domain of histone H3 [4,5] and that resembles the yeast centromeric component CSE4 [6]. We have found by simultaneous immunofluorescence with centromere antigens of known ultrastructural location that CENP-A is concentrated in the region of the inner kinetochore plate at active centromeres. Because CENP A was previously shown to co-purify with nucleosomes [7], our data suggest a specific nucleosomal substructure for the kinetochore. In human cells, these kinetochore-specific nucleosomes are enriched in alpha-satellite DNA [8]. However, the association of CENP-A with neocentromeres lacking detectable alpha-satellite DNA, and the lack of CENP-A association with alpha-satellite-rich inactive centromeres of dicentric chromosomes together suggest that CENP-A association with kinetochores is unlikely to be determined solely by DNA sequence recognition. We speculate that CENP-A binding could be a consequence of epigenetic tagging of mammalian centromeres.", 
"A programme of research into phase change in the desert locust, Schistocerca gregaria, is described. The ability to change phase between solitarious and gregarious forms in response to population density is a key feature of locusts and is central to their occasional yet catastrophic impact on humans. Phase polymorphism is an extreme form of phenotypic plasticity. The most labile phase characteristic is behaviour. It is argued that a fully integrated study of behavioural phase change provides a powerful tool for understanding both the mechanisms of phase change and locust population dynamics, both of which offer possibilities for improved management and control. of desert locust plagues. An assay for measuring behavioural phase-state in individual locusts was derived, based on logistic regression analysis. Experiments are described that used the assay to quantify the time-course of behavioural change, both within the life of individual locusts and across generations. The locust-related stimuli that provoke behavioural gregarization were investigated. Complex interactions were found between tactile, visual and olfactory stimuli, with the former exerting the strongest effect. Behavioural analysis also directed a study of the mechanisms whereby adult females exert an epigenetic influence over the phase-state of their developing offspring. Female locusts use their experience of the extent and recency of being crowded to predict the probability that their offspring will emerge into a high-density population, and alter the development of their embryos accordingly through a gregarizing agent added to the foam that surrounds the eggs at laying. There is also a less pronounced paternal influence on hatchling phase-state. An understanding of the time-course of behavioural phase change led to a study of the effect of the fine-scale distribution of resources in the environment on interactions between individual locusts, and hence on phase change. This, in turn, stimulated an exploration of the implications of individual behavioural phase change for population dynamics. Cellular automata models were derived that explore the relationships between population density, density of food resources and the distribution of resources in the environment. The results of the simulation showed how the extent of gregarization within a population increases with rising population size relative to food abundance and increasing concentration of food resources. Of particular interest was the emergence of critical zones across particular combinations of resource abundance, resource distribution and population size, where a solitarious population would rapidly gregarize. The model provided the basis for further laboratory and field experiments, which are described.", 
"Acquired epigenetic modifications, such as DNA methylation or stable chromatin structures, are not normally thought to be inherited through the germline to future generations in mammals [1,2]. Studies in the mouse have shown that specific manipulations of early embryos, such as nuclear transplantation, can result in altered patterns of gene expression and induce phenotypic alterations at later stages of development [3-5]. These effects are consistent with acquired epigenetic modifications that are somatically heritable, such as DNA methylation. Repression and DNA methylation of genes encoding major urinary proteins, repression of the gene encoding olfactory marker protein, and reduced body weight can be experimentally induced by nuclear transplantation in early embryos M. Strikingly, we now report that these acquired phenotypes are transmitted to most of the offspring of manipulated parent mice. This is the first demonstration of epigenetic inheritance of specific alterations of gene expression through the germline, These observations establish a mammalian model for transgenerational effects that are important for human health, and also raise the question of the evolutionary importance of epigenetic inheritance. (C) Current Biology Ltd.", 
"The pathway of molecular interactions leading to kinetochore assembly on mammalian chromosomes is unknown. Kinetochores could be specified by structural features of centromeric satellite DNA [1-3] or by specific DNA sequences, analogous to budding yeast centromeres, interspersed in centromeric satellite DNA arrays [4,5]. Alternatively, kinetochores could be epigenetic structures that replicate without strict dependence on DNA sequence [6-8]. We purified kinetochore-associated chromatin from human chromosomes by immunoprecipitation of CENP-A, a centromere-specific histone H3 homologue located in the inner plate of the kinetochore [6,9,10]. Hybridization and DNA sequence analyses of cloned kinetochore DNA fragments revealed alpha-satellite as the predominant sequence associated with CENP-A. A major site of micrococcal nuclease digestion was identified by mapping the termini of alpha-satellite clones, suggesting that the inner kinetochore plate contains phased arrays of CENP-A-alpha-satellite nucleosomes. These experiments demonstrate for the first time that complex satellite DNA is a structural component of the kinetochore. Further, because complex satellite DNA is evolutionarily unconserved, these results suggest that molecular recognition events necessary for kinetochore formation take place at the level of DNA conformation or epigenetic mechanisms rather than DNA sequence per se.", 
"Purpose: This report reviews the data obtained in the author's laboratory over the past two decades, which support the hypothesis that radiation can induce a genome-wide process of instability in mammalian cells that is transmitted over many generations of cell replication leading to an enhanced frequency of genetic changes occurring among the progeny of the original irradiated cell. Methods: Endpoints examined are malignant transformation, delayed reproductive failure, chromosomal aberrations and mutagenesis; the relationship between these endpoints is not clear. Results: The instability phenotype was induced in approximately 10-20% of the irradiated cell population with doses of 4-12 Gy, and may be induced by much smaller doses. Mutational instability can be induced by either X-rays or ct-particles; the spectrum of DNA structural changes in mutations arising in such unstable populations differed significantly from that for direct radiation-induced mutations. Evidence is also presented for the occurrence of coincident mutations, further supporting the existence of a genome-wide process of hypermutability. Finally, data suggest that epigenetic factors acting in the host may significantly influence the development of genomic instability in vivo. Conclusions: It appears that radiation can induce a type of genomic instability in mammalian cells that is transmissible to their progeny. There remain, however, many unanswered questions concerning this phenomenon, in particular how it is initiated and how it is maintained over many generations of cell replication.", 
"There have been allegations in the media and in the courts that cell phones and other types of hand-held transceivers are a cause of cancer. There have also been numerous public objections to the siting of TV, radio and cell phone transmission facilities because of a fear of cancer induction. A recent publication in Radiation Research by Repacholi et al, (147, 631-640, 1997) which suggests that exposure to radiofrequency (RF) radiation may increase lymphoma incidence in mice has contributed to this controversy. The goal of this review is to provide biomedical researchers a brief overview of the existing RF radiation-cancer studies. This article begins with a brief review of the physics and technology of cell phones, It then reviews the existing epidemiological studies of RF radiation, identifying gaps in our knowledge. Finally, the review discusses the cytogenetics literature on RF radiation and the whole-animal RE-radiation carcinogenesis studies, The epidemiological evidence for an association between RF radiation and cancer is found to be weak and inconsistent, the laboratory studies generally do not suggest that cell phone RF radiation has genotoxic or epigenetic activity, and a cell phone RF radiation-cancer connection is found to be physically implausible. Overall, the existing evidence for a causal relationship between RF radiation from cell phones and cancer is found to be weak to nonexistent. (C) 1999 by Radiation Research Society.", 
"Recent work with plants has demonstrated that genome instability can be triggered by a change in chromosome number arising from either whole genome duplications (polyploidy) or loss/gain of individual chromosomes (aneuploidy). This genome instability is manifested as rapid structural and epigenetic alterations that can occur somatically or meiotically within a few generations after heteroploid formation. The intrinsic instability of newly formed polyploid and aneuploid genomes has relevance for genome evolution and human carcinogenesis, and points toward recombinational and epigenetic mechanisms that sense and respond to chromosome numerical changes. (C) 1999 John Wiley & Sons, Inc.", 
"Purpose: To review studies of radiation-induced genomic instability in haemopoietic cells. Major findings: Studies have demonstrated a high frequency of non-clonal, cytogenetic abnormalities in the clonal descendants of alpha-particle-irradiated (approximately one track per cell) primary murine and human haemopoietic stem cells in vitro. The induction of this phenomenon has a strong dependence on the genetic characteristics of the cells and is transmissible in vivo following transplantation of alpha-irradiated mouse bone marrow. In clonogenic cell cultures of alpha-irradiated haemopoietic cells, there is also an increased incidence of hprt mutations and an increased incidence of apoptosis. These effects may be regarded as the consequences of a destabilization of the genome collectively termed radiation-induced genomic instability. Instability is induced at very high frequencies suggesting that epigenetic changes may be a common underlying mechanism. Consistent with this suggestion is the finding of an enhanced and persisting oxy-radical activity in the descendants of irradiated stem cells, which is consistent with oxidative stress being an important feature of the mechanism(s) underlying the persistence of instability in haemopoietic cells. Recent studies have revealed that more clonogenic cells than are actually traversed by an alpha-particle are able to express the instability phenotype. These data are consistent with unexpected interactions between irradiated and nonirradiated cells but the mechanism of initiation of instability is not understood.", 
"Epigenetic inheritance systems enable the environmentally induced phenotypes to be transmitted between generations. Jablonka and Lamb (1991, 1995) proposed that these systems have a substantial role during speciation. They argued that divergence of isolated populations may be first triggered by the accumulation of (heritable) phenotypic differences that are later followed and strengthened by genetic changes. The plausibility of this idea is examined in this paper. At first, we discuss the exploratory behaviour of an epigenetic inheritance system on a one peak adaptive landscape. If a quantitative trait is far from the optimum, then it is advantageous to induce heritable phenotypic variation. Conversely, if the genotypes get closer to the peak, it is more favorable to canalize the phenotypic expression of the character. This process would lead to genetic assimilation. Next we show that the divergence of heritable epigenetic marks acts to reduce or to eliminate the genetic barrier between two adaptive peaks. Therefore, an epigenetic inheritance system can increase the probability of transition from one adaptive state to another. Peak shift might be initiated by (i) slight changes in the inducing environment or by (ii) genetic drift of the genes controlling epigenetic variability. Remarkably, drift-induced transition is facilitated even if phenotypic variation is not heritable. A corollary of our thesis is that evolution can proceed through suboptimal phenotypic states, without passing through a deep adaptive valley of the genotype. We also consider the consequences of this finding on the dynamics and mode of reproductive isolation. (C) 1999 Academic Press.", 
"An isologous diversification theory for cell differentiation is proposed, based on simulations of interacting cells with biochemical networks and the cell division process following consumption of some chemicals. According to the simulations of the interaction-based dynamical systems model, the following scenario of the cell differentiation is proposed. (1) Up to some threshold number, divisions bring about almost identical cells with synchronized biochemical oscillations. (2) As the number is increased, the oscillations lose synchrony, leading to groups of cells with different phases of oscillations. (3) Amplitudes of oscillation and averaged chemical compositions start to differ by groups of cells. The differentiated behavior of states is transmitted to daughter cells. (4) Recursivity is formed so that the daughter cells keep the identical chemical character. This ''memory'' is made possible through the transfer of initial conditions. (5) Successive differentiation proceeds. The mechanism of tumor cell formation, origin of stem cells, anomalous differentiation by transplantations, apoptosis and other features of cell differentiation process are also discussed, with some novel predictions. (C) 1997 Society for Mathematical Biology", 
"A mutation that disrupts post-transcriptional gene silencing in Neurospora crassa has been found to affect the homologue of a plant-encoded RNA-dependent RNA polymerase. This enzyme may produce a specificity determinant of gene silencing and mediate an epigenetic conversion at the RNA level.", 
"Isologous diversification, proposed for cell differentiation, is shown to be stable against molecular and other external fluctuations, where amplification of noise-induced slight difference between cells leads to a noise-tolerant society with differentiated cell types. It is a general consequence of interacting cells with biochemical networks and cell divisions, as is confirmed by several model simulations. According to the theory, differentiation proceeds first by loss of synchrony of intracellular oscillations as the number of cells increases. Then the chemical composition of the cells is differentiated. The differentiated compositions become inherited by the next generation, and lead to determined cell types. As a result of successive occurrence of the cell differentiation, the cell society will be composed of different cell types. The whole developmental process is robust not only against molecular fluctuations but also against the removal of a cluster of cells. This robustness is a remarkable feature of isologous diversification, in contrast to the conventional threshold-type mechanism for development. As a testable consequence of the theory, we also discuss interaction-dependent tumor formation and negative correlation between growth speed and chemical diversity. (C) 1999 Academic Press.", 
" ", 
"Four cases of paramutation and gene silencing in plants differ in their genetic properties, but each may Involve epigenetic interactions between transposable elements.", 
"The delayed expression of cell death in progeny of irradiated survivors was christened 'lethal mutations' by Tikvah Alper in 1984. The effect occurs when clones, or populations of cells grown up from irradiated progenitor cells, are replated and reassessed for cloning efficiency or population doubling time. The effect has been shown to be associated with the low dose shoulder region of the survival curve and is due to events occurring in the first two hours post irradiation, i.e. the 'fast repair' period. In this review the lethal mutation data accumulated over the past ten years is discussed in relation to our modern understanding of cellular and molecular events in radiation carcinogenesis and genomic instability research. It is suggested that lethal mutations are associated with a general epigenetic or field effect occurring in all irradiated cells, which makes them more prone to mutations, some of which are lethal. The implications of this for our current approach to risk estimates and therapeutic dose calculation, need to be addressed.", 
"The adaptive value of epigenetic inheritance systems is investigated in a simple mathematical framework. These systems enable the environmentally induced phenotypes to be transmitted between generations. The frequencies of the different epigenetic variants are determined by the plasticity and the efficiency of transmission (called memory). Plasticity and memory are genetically determined. This paper studies the evolution of a quantitative character, its plasticity and memory, on the adaptive landscape. Due to the dual inheritance of the character, selection acts on two revels: on the phenotypes of the same genotype, and on the different genotypes. Plasticity generates the raw material, and memory increases the strength of phenotypic selection. If the character is far from the peak of the landscape, then dual inheritance of the character can be advantageous for the genotype. Near the peak it is more favourable to suppress phenotypic variation. This would lead to genetic assimilation.", 
"Epigenetic regulation of transcription can lead to a stable differential expression of identical genetic information in the same cell or cell population. There is increasing evidence that higher order chromatin structures, involving specific multiprotein complexes, constitute one device to establish and maintain epigenetic marks. In addition, defined chromosomal elements conferring epigenetic inheritance of transcriptional expression states have recently been identified. During the period where the difference in expression of identical genes is established, these sequences appear to be used as switch elements by both negative and positive regulators. Once the epigenetic mark is set, the elements maintain either the silenced or the activated expression state over many cell generations. Here we review recent data obtained from analyzing epigenetic gene regulation in different organisms and show that similarities in the underlying mechanisms appear to exist. BioEssays 21:824-832, 1999. (C) 1999 John Wiley & Sons, Inc.", 
"Expression and transposition of the Suppressor-mutator (Spm) transposon of maize are controlled by interacting epigenetic and autoregulatory mechanisms. Methylation of critical element sequences prevents both transcription and transposition, heritably inactivating the element. The promoter, comprising the terminal 0.2 kb of the element, and a 0.35-kb, highly GC-rich, downstream sequence are the methylation target sequences. The element encodes two proteins necessary for transposition, TnpA and TnpD. There are multiple TnpA binding sites, both in the 5' terminal promoter region and at the element's 3' end. In addition to its role in transposition, TnpA is both a positive and a negative regulator of transcription. TnpA represses the element's promoter when it is not methylated. When the element is inactive and its promoter methylated, TnpA activates the methylated promoter and facilitates both its transient and heritable demethylation.", 
"Intracytoplasmic sperm injection (ICSI) is the latest, and by far the most efficient, variant of micromanipulation-assisted fertilization, whereby a single spermatozoon is selected, aspirated into a microinjection needle and injected to the oocyte cytoplasm. The development of this technique is mainly linked to application in human assisted reproduction for which it enables fertilization with defective spermatozoa that would not otherwise be able to penetrate an oocyte by their proper means. Because ICSI by-passes many steps of the natural fertilization process, it offers an extremely interesting model for the study of basic mechanisms underlying fertilization. This is particularly true for oocyte activation, whose mechanism needs to be revisited in light of the current ICSI research. The massive application of ICSI in human infertility treatment also represents a huge laboratory in which the impact of different genetic and epigenetic anomalies of the male gamete on fertilization and embryonic development can be studied. (C) 1999 John Wiley & Sons, Inc.", 
"The major paradigm for mathematically describing the carcinogenic process has been through the use of multistage models. Multistage models are made up of numerous compartments representing cells in various stages on the way to malignancy and where movement from one cell class to another is assumed to have exponential waiting time. Once a cell is in a particular class, clonal expansion through a linear birth-death process increases the size of the compartment, These models are characterized by movement of single cells from one compartment to another rather than clonal colonies of cells. However, there is some evidence to suggest that, in certain organs for certain types of agents, preneoplastic lesions with different phenotypes arise directly from an entire clonal colony rather than from a single cell within that colony. This manuscript describes a simple mathematical model of carcinogenesis using both persistent changes of single or several cells (to start the process) and shifting of colonies to describe the stages of the model. Likelihoods for the use of the model with data on colonies of preneoplastic lesions are described and applied to real data. (C) 1998 Elsevier Science Inc. All rights reserved.", 
"Cortical maps often contain global spatial structure; however, theoretical accounts for their development have generally concentrated on reproducing only local structure. We show that the elastic net model of cortical map formation can closely approximate the global structure of the ocular dominance column map observed in macaque primary visual cortex. A key component is the assumption of spatially non-uniform and anisotropic correlations in the retina. This work shows how genetic and epigenetic effects could combine to establish characteristic global structure in cortical maps.", 
"The formation of silent epialleles is accompanied by local hypermethylation of the DNA template, and genetically altered, methylation-deficient Arabidopsis mutants generate an increased number of epimutations. But what came first - methylation or epigenetic change? (C) Current Biology Ltd ISSN 0960-9822.", 
"Genomic imprinting is an epigenetic mechanism resulting in the preferential expression of the maternal or paternal alleles of a specific subset of genes in the mammalian genome. A key but relatively unexplored question is how imprints are established in the germline. New observations((1)) on two classical imprinting disorders, the Prader-Willi (PWS) and Angelman (AS) syndromes, offer the first genetic insight into this process. Molecular analysis of imprinting mutations that interfere with the appropriate establishment of the maternal and paternal epigenotypes has led to the identification of imprinted transcripts that could be involved in switching imprints in the germlines.", 
"In the mammalian brain dopamine systems play a central role in the control of movement, hormone release, emotional balance and reward. Alteration of dopaminergic neurotransmission is involved in Parkinson's disease and other movement disorders, as well as in some psychotic syndromes. This review summarises recent findings, which shed some light on signals and cellular interactions involved in the specification and maturation of the dopaminergic function during neurogenesis. In particular we will focus on three major issues: (1) the differentiation of dopaminergic neurones triggered by direct contact with the midbrain floor plate cells through the action of sonic hedgehog; (2) the neurotrophic factors acting on dopaminergic neurones; and (3) the role of target striatal cells on the survival and the axonal growth of developing or grafted dopaminergic neurones.", 
"Studies of regeneration research has a very profound historical background, longer than genetics and embryology per se. In this article, I have tried to make clear the importance of the discovery of Niazi on the effect of vitamin A on amphibian limb regeneration in the long tradition of regeneration study. His discovery is truly one of the main milestones in recent era of the field. It revitalized the study of regeneration, in particular the problem of replication of pattern, A more recent discovery of heteromorphic regeneration in tadpoles elicited by vitamin A by Mohanty-Hejmadi is also of a great historical significance. It has opened the way to investigate the most mysterious phenomena known from early 20th in modern eyes, most probably in terms of the epigenetic switch of homeotic genes.", 
"We have previously shown that primary explant cultures of human urothelium exposed to low doses of gamma-radiation subsequently accumulate a high level of stable p53 but it was not clear from those studies whether this protein stabilization occurred through an event in another gene involved in p53 protein control or possibly an epigenetic event. In these experiments, primary urothelial cultures from five different patients were exposed to either 0.5 or 5 Gy gamma-radiation from a (60)Cobalt source and allowed to grow for 7-10 division cycles to allow development of any radiation-induced, non-lethal changes in the cells. C-myc, Bcl-2 and stable p53 proteins were found to be elevated in cultures following both radiation doses. PCR-SSCPE analysis of the p53 gene was performed on cultures in order to determine whether genetic mutations could be the underlying basis for persistent increased stable p53 expression. Following 0.5 Gy exposure, the cultures also developed multiple distinct 'foci' of rapidly dividing cells which strongly overexpressed p53. These grew on a background of morphologically normal cells. When such foci were selectively analysed for their p53 mutation status by PCR-SSCPE, there was evidence that they contained cells which had developed changes to the p53 gene postirradiation. These changes appeared to occur more frequently in focal cells than in cells of normal morphological appearance in the same culture. These results may have mechanistic importance given the controversy regarding low-dose radiation effects and p53-related genomic instability.", 
"Purpose: The purpose of this review is to assess the effect of radiation-induced mutation on genes subject to genomic imprinting, and the consequences of this on the understanding of genomic instability. Genomic imprinting is the phenomenon in which one of the two alleles of a gene is expressed or suppressed depending on the gamete from which it was inherited, thus effectively rendering a cell hemizygous for the expression of certain key genes. The consequence of this is that such loci are potentially more likely targets for mutagenesis since one allele is normally inactive. This is not only important in the recognition of a subgroup of target genes for radiation-induced damage, but also raises the possibility of mutations affecting the epigenotype of key tumour suppressor or tumour promoting genes. Such mutations may in principle affect the stability of imprinting and may fall into a novel class of 'epimutation', where the DNA sequence is not affected, but post-transcriptional mechanisms of epigenotype maintenance are stably altered. These novel mechanisms are discussed in relation with radiation-induced genomic instability and the heritability of tumour predisposition from radiation-exposed parents. Conclusions: As yet there is only circumstantial evidence that the targets for radiation-induced DNA and epigenetic damage are imprinted genes, or genes involved in the maintenance of the epigenotype. However, the potential consequences of such genes being important targets for the generation of genomic instability or other forms of damage are serious and could affect the interpretation of the risks of low dose radiation exposure and of epidemiological data.", 
"The cell property of processing the environmental information is called sensitivity and referred to a ''sensitive'' cell system in which physical signals and specialized molecules work in relation to peculiar cell structure. It is suggested that, in addition to its role in cell behaviour, the sensitive system performs a basic role in morphogenesis in all cells. It interacts with the genetic system in gene expression and regulation directly or indirectly through epigenetic processes. Epigenetic inheritance, adaptive mutations and genetic assimilation allow environmental information to be embodied in new traits, thereby becoming relevant in evolution. This is consistent with an evolutionary mechanism with two alternate and recurrent phases: the first, epigenetic and Lamarckian at cell and organism levels and the second, selective and Darwinian, at population level.", 
"Genomic imprinting is an epigenetic marking process that confers parent-of-origin-dependent expression on certain genes. These imprinted genes are sometimes found in clusters, suggesting a possible involvement of higher order regulatory elements controlling expression and imprinting of genes organised in such clusters. In the distal chromosome 7 there are at least four imprinted genes: Mash2, lns2, lgf2 and H19. Recent evidence((1)) suggests that imprinting and expression of at least lgf2 and H19 may be mechanistically linked.", 
"The Gaia theory states that the whole surface layer of the globe, including organisms, atmosphere, hydrosphere and lithosphere, can be viewed as a self-evolving homeostatic system. Bacteria play a principal role in this formative process. This line of thinking should answer several questions: Is the biosphere simply a set of essentially selfish individuals, each testing its fitness? Is memory in the biosphere confined to genes? Is the composition of ecosystems and their behaviour only kind of dynamic equilibrium? Or is there a huge amount of epigenetic information that enables organisms to interpret properly their situation and behave accordingly? It is suggested here that it is the information flow, rather than pure thermodynamics and natural selection, that enables living beings not only to ''read'' their environment, interpret their situation and behave accordingly to this understanding, but also to establish geophysiology, to become part of Gaia. This flow comprises genes as well as signals, diffusible as well as permanent. From an analogy with the situation in the multicellular organism, three types of information mediators inside the body of Gaia are suggested: ultrastructure, diffusible signals and gene flux. With a shared gene pool, intricate ultrastructure and quickly diffusible signals, it is legitimate to consider Gaia a superorganism with an ontogeny. (C) 1995 Academic Press Limited", 
"The methylation of 5'CpG 3' dinucleotides within genes creates potential targets for protein complexes that bind to methylated DMA sequences and to histone deacetylases (MBD-HDAC). This can lead to transcriptional repression by modification of chromatin. To test the importance of this repression in vivo and to determine when during development these epigenetic controls are placed on genes, two novel genes have been engineered by directed mutagenesis of the CpG-rich LacZ gene that are depleted of (LagZ) or completely lacking (LagoZ) CpG sequences. We report that the expression (transcriptional and translational) of the three genes is indistinguishable in transient assays in cleaving mouse embryos. Therefore, the complete absence of CpG sequences within three kilobases of coding sequence is compatible with its maintenance in the nucleus and with its expression. These molecules can now be used to study the ontogenesis of the CpG-dependent repressive system in intact organisms. (C) 1999 Academie des sciences/Editions scientifiques et medicales Elsevier SAS.", 
"Multiple steady-state levels of autoregulatory transcription factors constitute alternative epigenetic states, and could help specify the heritable phenotype of an organism. In this work, the inheritance of autoregulatory transcription factors through sexual reproduction is modeled to determine the conditions under which different alternative epigenetic states become fixed in a population. The influence of transient environmental perturbations on the fixation of states is discussed in the context of speciation. (C) 1995 Academic Press Limited", 
"Odorant receptor genes reveal a new case oi monoallelic expression: just one allele of one oi the large number oi receptor genes appears to be transcribed in a given sensory neuron.", 
"Inappropriate estrogen exposure during critical periods of development will cause numerous abnormalities in the female reproductive tract. Epigenetic effects on the expression of estrogen-regulated genes is proposed to be one of the mechanisms by which neonatal estrogen elicits teratogenic and carcinogenic effects. Of note is the existence of an integral relationship between the regulation of members of the epidermal growth factor (EGF) gene family and estrogen effects on the growth and differentiation of the reproductive tract. To determine whether the EGF gene family plays a critical role in mediating the pathogenic effects of estrogen, we have used transforming growth factor-alpha (TGF alpha) transgenic mice to investigate the effects of constitutive TGF alpha expression in the reproductive tract and whether TGF alpha would potentiate carcinogenesis induced by the potent estrogen, diethylstilbestrol (DES), and by the carcinogen 7,12-dimethylbenz[a]anthracene (DMBA). The animals were homozygous TGF alpha transgenic female mice from the MT42 line and the parental CD-1 outbred mice. Constitutive TGF alpha expression was found to augment the effects of both DES and DMBA in eliciting hyperplastic and differentiation changes in the reproductive tract. The presence of the TGF alpha transgene significantly increased the incidence of DES-induced vaginal adenosis, uterine endometrial hyperplasia, hypospadia, and benign ovarian cysts. In addtion, TGF alpha potentiated the effects of DMBA in eliciting uterine polyps and benign ovarian cysts, and in the retention of Wolffian Duct remnants. However, the incidence of reproductive tract neoplasia was not promoted by the presence of the TGF alpha. transgene. This study indicates that TGF alpha plays a role in the developmental and morphogenic events of both the Mullerian duct and urogenital sinus, and that deregulation is associated with pathogenesis of these tissues. Furthermore, the fact that constitutive expression of the TGF alpha did not substitute for DES as a reproductive tract carcinogen or act as a promoter of DES-induced uterine neoplasia suggest that DES carcinogenesis involves more than aberrant expression of this single growth factor.", 
"The course and outcome of biological evolution is strongly influenced by constraints. They, flanking the work of natural selection, operate not only by limiting but also by changing the evolutionary processes. The following constraint categories are discussed and analyzed: structural developmental, phylogenetic, genetic, epigenetic, behavioural, ecological (as ecosystemic) and selective. Epigenetic, behavioural and ecosystemic constraints may be important ways through which an environmental information, supplementary to that conveyed by natural selection, can flow in the evolutionary process influencing the phenotype construction. The different constraint categories depend on three basic evolutionary forces: structure, environment and history or contingency. They form a network of reciprocal dependences and interact with natural selection. In the newly proposed two-step evolutionary model (Sara [1993]), in which two phases alternate at each generation, the constructive, organismic phase is represented by constraints (except the selective ones) while the selective, populational phase is represented by natural selection and selective constraints as drift.", 
"The meaning of hereditary information is not simple. It includes not only what a system receives and transmits but particularly what it makes. The syntactic basis to hereditary information is also not straightforward. For example, is DNA instructions, or data, or both? The answer to this question requires an appreciation of the meaning of the information yet there are a number of possible semantic systems for describing hereditary information including proteins and development. The descriptive boundaries of hereditary information are examined by locating some general organising themes including hierarchy; ecology, regulation, epigenetic systems and talkback. Though metaphors have limits in terms of their explanatory power, a number have influenced the development of biological thinking and biosystems have variously been represented as chemical laboratories, computers, electromechanical machines and societies. In this article a further metaphor is discussed, that of life-as-a-play or dance in which the trio of script (genome), cast (metabolism) and stage (cellular structure) co-exist and pre-exist the phenotypic life history which inherits them. A fuller examination of this trio provides an important perspective on the study of the organisations of information processing in hereditary systems. Copyright (C) 1997 Elsevier Science Ireland.", 
" ", 
"The combination of hierarchical constraints and compartmentalization provides a material basis for cells to 1) modulate the magnitude and duration of genome self-modification and 2) to restrict induced variation to defined regions of the genome. The hypothesis is presented that long-range coherence between genomic self-modification events and cytoplasmic activities can regulate and even divert genomic reorganizations. Finally it is proposed that two formal causes acr in phylogeny, one being the genome which encodes an ontogeny and the second being the organismal epigenetic attractors which act as boundary conditions on permissible genomic change. Genome self-modification can thus be viewed as a means for early epigenesis to modify genomic programs.", 
"In two Artemia wild-type sibling species originating from the Old and New Worlds, the processes underlying the construction of the naupliar body during embryonic development and the construction of the adult body during postembryonic development are disrupted by specific nutritional deficiencies and/or the administration of metabolic inhibitors. The species-specific phenotypic outcomes of these experimental disruptions on the construction of segments and the establishment of their identity, permit us to outline a model in which Hox genes would act as intermediary cogwheels fastened to a mechanism put in gear upstream by purine-mediated processes which would trigger downstream folic acid-mediated processes. The prevalent view that Hox genes can select for different developmental programmes, is challenged by this model whose relevancy is analysed in the context of our present knowledge on the master functions ascribed to Hox genes in developmental and evolutionary processes, ((C) Academie des sciences / Elsevier, Paris.)", 
"The objective of this study was to gather insights and compare the mode of action of the non phorbol, diterpene mezerein with the phorbol ester, phorbol-12-myristate-13 acetate, in normal and transformed cells. Both phorbol-12-myristate-13 acetate and mezerein are shown to activate the signal transduction pathways involving post translational modification of proteins by poly ADP-ribosylation and by protein kinase C, but to varying extents and showed different time kinetics and cell type differences, Multiple nuclear proteins, especially histones H3d, A24 and H1 served as accepters of poly ADP-ribose in response to PMA in both NIH 3T3 and HDCS cells whereas H1 and H2B were the major accepters in case of mezerein treatment, similarly in both NIH 3T3 and HDCS cells. The results suggest an epigenetic mechanism(s) in tumour promotion by mezerein.", 
"The molecular cell sciences have had a great impact in the analysis of the genetic and epigenetic events of esophageal and gastric tumorigenesis. In other regions of the alimentary tract such as the colon, the serial identification of the molecular events in the corresponding morphological lesions is perhaps most advanced. This is, in part, due to the relative ease of the histological characterisation of the premalignant lesions. In this regard the analysis of morphological and molecular adaptation in the alimentary tract is inextricable. This review aims, therefore, to judiciously assess the relative applications of contemporary techniques in investigative histopathology. (C) 1995 Wiley-Liss, Inc.", 
" ", 
" ", 
" ", 
" ", 
" ", 
"In order to understand the complex ontogenetical processes, the development of Streptomyces (S.) griseus was applied as a model. The developmental cycle of S. griseus starts and ends as a conidium. In between, coenocytic mycelium develops which, if studied by cytomorphological of biochemical methods, exhibits conspicious heterogeneity. The hyphae develop into young, transient and old vegetative hyphae and different stages of reproductive forms. In developmentally blocked mutants these sequences of events appear mixed in all possible associations. It seems as if the program of development could be divided into several subprograms. The quantitative evaluation of the results show that the individual morphological markers exhibit certain independence from each other realized with a given probability. The conidia of S. griseus are also heterogeneous concerning all morphological and physiological traits examined so far (shape, size, light refraction, staining and shape of nucleoids with Feulgen, methyl green - pyronine, intensity and form of polysaccharide distribution, heat resistance, etc.). Kinetics of the survival curves of two S. griseus strains - a well-sporulating and its developmentally blocked nutant /24/ - are different from each other, one has many more heat resistant conidia than the other but the kinetics of the survival curves of the two S. griseus strains indicate that spore populations of both react differently to heat treatment and heat resistance can be modeled by assuming the presence of two independent subpopulations of spores with different heat sensitivity. The emergence of two distinct subpopulations with (possibly) the same genetic make-up is designated: phenotypic segregation. Heat resistance is first of all species specific (genetically determined) but the epigenetic segregation seems to be characteristic of the developmental process. This process can in certain mutants be affected by environmental conditions and more importantly by the so-called autoregulators (A-factor and factor C). Factor C and A-factor are needed to normal development, if their quantity or the time of addition to the culture was not optimal, the quantity of spares decreased.", 
" ", 
"Massive cell migration, proliferation, phenotypic differentiation, and enhanced biosynthetic activities characterize the sites of wound healing and fibrosis. Regulation of cellular functions by extracellular matrix, which consists of a dynamic assemblage of a variety of interacting molecules capable of reorganization in response to endogenous and exogenous stimuli, represents a fundamental epigenetic mechanism regulating cellular behavior and phenotype. Interactions of the individual components of extracellular matrix with specific cell surface molecules, integrin receptors, and proteoglycans initiate a cascade of signal transduction leading to varied short-term or persistent cellular responses. Extracellular matrix also serves as an important reservoir of cytokines and growth factors, thus modulating the action of a host of potent biological response modifiers by their selective, local accumulation and release. Currently known mechanisms by which extracellular matrix modulates different facets of the process of tissue remodeling after injury, which culminate either in normal wound repair or fibrosis, are discussed.", 
"Fluctuating asymmetry is an epigenetic measure of the ability of individuals to undergo identical development of a usually bilaterally symmetrical character on both sides of the body. Horns of beetles and spurs of birds are elaborate structures usually restricted to or enlarged in individuals of the limited sex and frequently used in intrasexual combat. Individuals with large horns usually win fights against individuals with small horns which suggests that horn size may reliable signal male fighting ability. A comparative study of the patterns of fluctuating asymmetry in horns of beetles and spurs of birds showed that the degree of asymmetry in these secondary sex traits was considerably larger than in elytra and wing length. which are apparently not subjected to sexual selection. There was a negative relationship between the degree of asymmetry and size of the secondary sex trait while the relationship for elytra and wing length was flat or U-shaped. This demonstrates that horn and spur size may reliable reflect male quality as determined by the degree of fluctuating asymmetry.", 
" ", 
" ", 
"Fundamental, yet unresolved, issues in developmental neurobiology concern the relative influence of genetic vs. epigenetic factors in determining cell phenotype and establishing positional relationships among clonally related cells in the developing and mature vertebrate central nervous system (CNS). Advances in our understanding of how cells acquire their identity awaited a means to introduce lineage tracers into dividing cells of the developing CNS where the progenitor cells, which are situated in a neuroepithelial layer adjacent to the ventricles, generally are small and inaccessible. The technique of retroviral-mediated gene transfer, whereby a heritable, easily detectable marker such as the gene for lacZ is integrated into the DNA of individual progenitor cells, has been used to analyze the lineage relationships of cells in the CNS and to derive the types of progenitor cells in the proliferative zones at different developmental stages. Collectively, these studies indicate that the CNS uses more than one strategy to achieve cell diversity. The analysis of the phenotypic composition of the cells within a clone indicates that there are predominantly separate progenitor cells for each of the main cell types comprising the cerebral cortex by the onset of cortical neurogenesis, although in other systems mostly multipotential progenitor cells persist throughout neurogenesis. Here I will compare and contrast the inferred role of cell lineage in the developing cerebral cortex and olfactory bulb, where postmitotic neurons migrate relatively long distances from their site of generation to their final destination, with that in other regions of the CNS in which the displacement of postmitotic neurons from their birthplace is significantly less.", 
"Evolutionary transitions to new levels of individuality have usually been treated as a part of the ''units of selection'' problem. It has previously been assumed that the unit of transmission and heritable variation at each level is the same-that it is the DNA base sequence and its variations. It is suggested here that considering the nature and the role of hereditary variations produced by non-DNA inheritance systems is essential for understanding some evolutionary transitions. The argument is illustrated by considering the role of epigenetic inheritance systems (EISs), the systems responsible for cellular memory, in the transition from unicellularity to multicellularity. It is argued that EISs played a vital role in the transition to multicellularity and the evolution of complex ontogenies, as well as having an important effect on the evolution of developmental strategies which protect the multicellular individual from disintegrating into its component parts. An analogy between the transition to multicellularity and the transition to a cultural unit integrated by language is also suggested.", 
" ", 
"Germinally transmissible variants that arise by the anomalous imposition of developmental information on the genome are not uncommon in plant genetics, although they are often ignored. Better understanding of such variants is believed to be important because they appear to reflect basic features of developmental control processes. This paper briefly reviews classical genetic studies of such variants in plants, then discusses recent work on the genetic behaviour of plant transgenes, the results of which parallel and extend the classical genetic studies of these phenomena. An attempt is made to explain the molecular basis of these phenomena in terms of modern hypotheses on the dynamic organization of chromatin.", 
"Variation in the branching morphologies of clonal plants, fungi, and sessile marine invertebrates is frequently correlated with a suite of life-history traits (e.g. 'phalanx' or 'guerilla'). These correlations have been interpreted to be the causal product of selection. A tacit assumption of selection on a trait is that development is canalized in the manner Waddington originally suggested for aclonal taxa, i.e. small perturbations in development result in a return to an equilibrial morphology. We tested this assumption by manipulating developing colonies of the hydroid Hydractinia echinata. The growth trajectory of these colonies follows a clone-specific schedule of production of three structures: feeding polyps, stolonal mat, and peripheral stolons. Isogeneic manipulations of the relative frequency of these structures show that developing colonies can regulate the rate of production of these three structures, but that regulation does not result in rapid convergence on a common growth trajectory.", 
"In an earlier work a model of the autocrine and paracrine pathways of tumor growth control was developed (Michelson and Leith. 1991. Autocrine and paracrine growth factors in tumor growth. Bull. math. Biol. 53, 639-656). The target population, a generic tumor, was modeled as a single, homogeneous population using the standard Verhulst equation of logistic growth. Mitogenic signals were represented by modifications to the Malthusian growth parameter and adaptational signals were represented by modifications to the carrying capacity. Three growth scenarios were described: (1) normal tissue wound healing, (2) unperturbed tumor growth, and (3) tumor growth in a radiation damaged environment, a phenomenon termed the Tumor Bed Effect (TBE). In this paper, we extend those results to include a ''triad'' of growth factor controls (autocrine, paracrine and endocrine) and heterogeneity of the target population. The heterogeneous factors in the model represent either intrinsic, epigenetic or environmental differences in both normally differentiating tissues and tumors. Three types of growth are modeled: (1) normal tissue differentiation or wound healing, assuming no communication between differentiated and undifferentiated cell compartments; (2) normal wound healing with feedback inhibition, due to signalling from the differentiated compartment; and (3) the development of hypoxia in a spherical tumor. The signal processing within the triad is discussed for each model and biologically reasonable constraints are defined for limits on growth control.", 
" ", 
"Epigenetic information, not DNA sequence, distinguishes different cell types within a multicellular organism. The molecular nature of epigenetic information specifying differentiated cell types is unknown. However, it must be stable over time and mitotically heritable. In this paper, steady-state levels of autoregulatory transcription factors are explored as a potential form of epigenetic information. In particular, a model autoregulatory transcription factor having two alternative stable steady-state levels is presented. Each steady-state level specifies a phenotypically distinguishable epigenetic state, analogous to a differentiated cell type. These states are mitotically stable if the transcription factor is inherited during cell division.", 
"Parental genomes in mammals are programmed in the germline with heritable epigenetic modifications that exert control on the expression of specific (imprinted) genes. DNA methylation is one form of epigenetic modification which shows marked genome-wide variations in the germline and during early development. Certain transgene loci also demonstrate (reversible) germline-specific methylation imprints that are heritable in somatic tissues during development. Recently, four endogenous genes have been identified whose expression is dependent on their parental origin. The mechanism of genomic imprinting and the role of imprinted genes during development is beginning to be analysed. Three of these genes map to the mouse chromosome 7. Human chromosomes 11p13, 11p15, and 15q11-13 are associated with disorders exhibiting parental origin effects in their patterns of inheritance. These regions share syntenic homology with mouse chromosome 7. The relationship between parental imprints, germline-dependent epigenetic inheritance and totipotency is also under investigation using embryonic stem cells derived from the epiblast. These cells are pluripotent or totipotent and evidence indicates the presence of at least the primary parental imprints. However, imprints inherited from the paternal germline in androgenetic cells are apparently more stable than those from the female germline in parthenogenetic cells.", 
"In Armadillidium vulgare, genetic variability at the mt DNA level has been studied to explain the nature of the mixed populations composed of genetic females (broods with sex ratio 1:1) and neo-females (female-biased broods). As a general rule, within a population, the restriction fragment patterns are well separated between the two categories of females. However, among populations, the same mitotype may correspond to both categories.", 
" ", 
"Halictine bees dig their nests into the earth. These bees include a few genus and numerous species which differ by ethological characteristics, some of them having reached a social way of life. They were studied both in the field and in large laboratory cages. In this first part, a summary of the biological cycle, the main problems treated and the results obtained are given for each of the studied species, classified from solitary to social ones. Evylaeus pallens is a solitary species with one annual exit of both sexes. Lasioglossum leucozonium is a solitary species with only one generation but two annual exits of females. Evylaeus villosulus is a solitary species with two generations and three annual exits of females. The following points are tackled: polymorphism of overwintering females; comparison, using eight characteristics, of the females in the two successive generations; sex ratio; longevity of overwintering females; cohabitation of several females in the same nest; biology of the summer generation. The size difference between the females of the two generations (7,4 per 100) and the low percentage of males produced in the first generation (21 per 100) might be regarded as preadaptations to a separation into castes. Halictus scabiosae is an often polygynous eusocial species with a poorly defined social polymorphism. Evylaeus calceatus, E. nigripes and E. albipes are three sibling eusocial species with two distinct broods; the first one is composed of workers (with more or less males), the second one of sexuals: future foundresses and big males. In E. calceatus, the following problems were dealt with : a) addition of pollen into the first brood cells: the volume of the pollen ball influences the sex of the egg laid on it: a weight threshold of sex determination can be brought out; b) large female individuals with foundress size but worker function are thus obtained: a dissociation between; size and caste is observed but no weight threshold of caste determination can be found; c) influence of temperature on the size of workers: the higher the temperature, the smaller the workers; d) polygny; e) replacement of the queen, before of after the emergence of the workers. E. nigripes produces less males in the first brood and a dissociation takes place between the provisioning of the cells and the egg-laying by the queen. According to populations, E. albipes shows a solitary form or a social form; the social level, in the latter, looks lower than in E. calceatus. Three grouped worker pupae evolved in a trigynous society, composed of an egg-layer and two pollen collectors and produced a lot of female offspring (73 per 100). Evylaeus marginatus is, so far, the only perenial known social species. Each foundress produces, year after year, in the same season, more and more workers; then, on the sixth year, she gives birth to sexuals: males and future foundresses in large numbers (> 500). The main problems dealt with in that species are social polymorphism, epigenetical determinism of the castes, analysis of the factors of socialization. The study of the biological features of these various species leaves us under the impression of a great diversity.", 
"A non-linear reaction diffusion model of a negative feedback epigenetic control system is presented. The model involves synthesis of the mitotic inducing and inhibiting proteins, simultaneously with intercellular self-diffusion and cross-diffusion of the latter only. The importance of negative cross-diffusion for creating a regular dissipative structure is shown. A bifurcation analysis of the non-linear diffusive system has been performed and it is concluded that bifurcation is supercritical. Lastly, using Liapunov's direct method, it is shown that the pattern evolved by the system is globally asymptotically stable.", 
" ", 
"Plant reproduction comprises an interlocking array of developmental pathways which include the formation of the sexual organs, the generation of germ lines de novo, and the operation of the mechanisms which regulate epigenetic imprinting and the system of self-incompatibility found in many angiosperms. Little is known of how these processes are regulated at a molecular level, with the exception of the floral organs which are determined by families of homeotic genes operating in a heterochronic fashion. In dioecious and monoecious plants the expression of these 'floral' genes must be modulated by sex-determination sequences, situated in some circumstances on sex chromosomes. Older, physiological data indicate that sex can be determined by growth regulators, particularly gibberellic acid (GA) and cytokinins, and it is possible that sex-determination genes establish local concentrations of growth regulators at the apex, which in turn influence the expression of the homeotic floral genes. Evidence from anther development indicates genes involved in differentiation of the male and female germ lines to be regulated by defined promoter, enhancer, and silencer regions, but few data are available on the sequences directing the initiation and regulation of meiosis; certainly parallels can be drawn with similar events in microorganisms, and useful complementation strategies may be devised, but significant differences do exist between yeasts and higher plants suggesting that more appropriate parallels should be drawn with multicellular eukaryotes such as nematodes. The loci involved in epigenetic imprinting and self-incompatibility are important because they affect both male and female developmental pathways. Nothing is known of the regulatory sequences which direct the epigenetic imprinting of the sperm and central cell genomes, but information is becoming available on the promoter regions of the S(incompatibility)-locus. Interestingly, sequences directing expression in male and female tissues are contained within a single 5' stretch within the locus, and these promoters also induce expression in different cell types in the anther and pistil depending on the type of self-incompatibility involved. Regulation of reproductive development in plants is apparently not very stringent, for there are examples in both male and female germ lines of reversion to an embryonic condition (apomixis and microspore embryogenesis); whether this reflects the highly dedifferentiated state of these cells or differences in the regulation of somatic and reproductive development remains to be determined.", 
"A non-linear reaction-diffusion model of the epigenetic system involving the synthesis and simultaneous intercellular self and cross-diffusion of the activator and inhibitor during embryogenesis has been proposed. It has been observed that the system spontaneously emerges into a stationary dissipative (Turing) structure only in the presence of positive cross-diffusion. That the stationary structure, thus envolved, has been shown to be globally asymptotically stable by using a suitable Liapunov's function.", 
"Teratocarcinomas are malignant tumors derived from germ cells or early embryonic cells that have undergone malignant transformation. To understand better the histogenesis of teratocarcinomas and related germ cell tumors, the process of tumorigenesis and the nature of tumor stem cells were studied in murine tumor models. Teratocarcinomas were produced by grafting early pregastrulation mouse embryos to extrauterine sites of syngeneic adult hosts. In the adult host many transplanted cells retained their embryonic phenotype. The adult organism could not control proliferation of these ostensibly normal embryonic cells which assumed the growth properties of malignant tumor cells. This malignancy developed without viral or chemical carcinogenesis and did not entail any genetic transformation. Retinoic acid and related morphogens induced differentiation and inhibited proliferation of teratocarcinoma stem cells. Likewise, teratocarcinoma stem cells inserted into the embryo were regulated by the developmental fields in control of proliferation of normal embryonic cells. These data show that in these cells malignancy can develop without irreversible genetic changes, that the malignant phenotype is reversible, and that proliferation of teratocarcinoma stem cells can be controlled by developmental fields regulating differentiation of equivalent normal cells. Murine teratocarcinoma derived from embryos is a prototype model for studies of epigenetic control of malignancy.", 
"Three types of phenotypic characters are recognized, which evolve without direct action of the selection but, however, could not be treated as selectively neutral (in commonly used meaning of the term). The first are characters with wide norm of reaction, which phenotypic expressions reproducibility depends on the information forthcoming from the environment. This includes ecological and ethological interactions between individuals: for instance, characters of the social component of the inheritance. The second are characters unreproducible at epigenetic level but having their own mechanisms of genetic reproduction. Self-replicating organelles serve as an example of such characters. The third, and commonest, set contains characters, which are reproducible only due to interaction of other phenotypic characters. Such are, for instance, morphogenetic interrelations causing complication of the spatial organization. Episelective evolution occurs as an indirect effect of independent selection of the characters, which are able to interact but are not united by either functional of morphogenetic correlations. It is supposed that essential portion of evolutionary phenomena usually attributed to the direct or correlative selective effects, emerges factually at the episelective level. The very possibility of episelective evolution is caused by relative independency of genetic and ontogenetic mechanisms of the reproduction of phenotypic characters.", 
"An intrathymic (i.t.) injection assay on B10.Thy-1 congenic mice was used to demonstrate that thymic prelymphoma cells developed first within mouse thymus 4 to 8 days after split-dose irradiation and were present in more than 63% of the test donor mice thymuses examined 21 and 31 days after irradiation. For the characterization of these thymic prelymphoma cells, thymocytes from BIO.Thy-1.1 mice sampled 1 mo after irradiation were stained with J11d mAb and mAb against TL-2 (thymus-leukemia) antigen which is not expressed on normal thymocytes of the BIO.Thy 1.2 and BIO.Thy 1.1 strains but does appear on thymocytes of split-dose irradiated mice. These cells were sorted into subpopulations, samples of which were injected into recipient thymuses to determine which subpopulations contained thymic prelymphoma cells. Results showed that thc prelymphoma cells were located in the J11d+TL-2+ cells. These prelymphoma cells were further characterized phenotypically as to their expression of the CD4 and CD8 antigens, which demonstrated that the thymic prelymphoma cells were present in the CD4-CD8- and CD4-CD8+ thymocyte subpopulations mainly and in the CD4+CD8+ subpopulation. The experiments on i.t. injection of a graded quantity of TL-2+ thymocytes from individual mice suggest that not all TL-2+ cells undergo neoplastic initiation and that prelymphoma cells may develop infrequently from one or more TL-2+ cells by genetic or epigenetic changes.", 
"Dose-response curves for chronic leukemia in A-bomb survivors and liver tumors in patients given Thorotrast (colloidal thorium dioxide) show large threshold effects. The existence of these threshold effects can be explained by the following hypothesis. A high dose of radiation causes a persistent wound in a cell-renewable tissue. Disorder of the injured cell society partly frees the component cells from territorial restraints on their proliferation, enabling them to continue development of their cellular functions toward advanced autonomy. This progression might be achieved by continued epigenetic and genetic changes as a result of occasional errors in the otherwise concerted healing action of various endogenous factors recruited for tissue repair. Carcinogenesis is not simply a single-cell problem but a cell-society problem. Therefore, it is not warranted to estimate risk at low doses by linear extrapolation from cancer data at high doses without knowledge of the mechanism of radiation carcinogenesis.", 
" ", 
"Several experimental results led to the hypothesis that odontoblast's and ameloblast's genetic programmes may determine a minimal number of cell cycles before overt differentiation can be triggered by specific, epigenetic, matrix-mediated interactions. The cell kinetic dependent maturation of the dental cells could imply transcriptional modifications of matrix molecules and paracrine factors involved in the control of the respective cytodifferentiations and of specific receptors confering competence to the responding cells.", 
" ", 
"The strategy of the evolutionary synthesis outlined in the works of I.I.Schmalhausen distinctly differs from the strategy adopted by the Synthetic Theory of Evolution. Schmalhausen's interpretation is mostly connected with the transitions from genetical to epigenetical levels, with the role of morphogenesis, with stabilizing selection and with mobility and stability in evolution. These problems are considered from the angle of the dynamic stability principle, which may be regarded as a universal evolutionary principle (VOROBYEVA, 1987; 1988; 1989).",
"MicroRNAs (mi-RNAs) are critical regulators of gene expression. Amplification and overexpression of individual 'oncomiRs' or genetic loss of tumour suppressor mi-RNAs are associated with human cancer and are sufficient to drive tumorigenesis in mouse models. Furthermore, global miRNA depletion caused by genetic and epigenetic alterations in components of the miRNA biogenesis machinery is oncogenic. This, together with the recent identification of novel miRNA regulatory factors and pathways, highlights the importance of miRNA dysregulation in cancer.", 
"PD-L1 and PD-1 (PD) pathway blockade is a highly promising therapy and has elicited durable antitumor responses and long-term remissions in a subset of patients with a broad spectrum of cancers. How to improve, widen, and predict the clinical response to anti-PD therapy is a central theme in the field of cancer immunology and immunotherapy. Oncologic, immunologic, genetic, and biological studies focused on the human cancer microenvironment have yielded substantial insight into this issue. Here, we focus on tumor microenvironment and evaluate several potential therapeutic response markers including the PD-L1 and PD-1 expression pattern, genetic mutations within cancer cells and neoantigens, cancer epigenetics and effector T cell landscape, and microbiota. We further clarify the mechanisms of action of these markers and their roles in shaping, being shaped, and/or predicting therapeutic responses. We also discuss a variety of combinations with PD pathway blockade and their scientific rationales for cancer treatment.", 
"We performed an extensive immunogenomic analysis of more than 10,000 tumors comprising 33 diverse cancer types by utilizing data compiled by TCGA. Across cancer types, we identified six immune subtypes-wound healing, IFN-gamma dominant, inflammatory, lymphocyte depleted, immunologically quiet, and TGF-beta dominant-characterized by differences in macrophage or lymphocyte signatures, Th1:Th2 cell ratio, extent of intratumoral heterogeneity, aneuploidy, extent of neoantigen load, overall cell proliferation, expression of immunomodulatory genes, and prognosis. Specific driver mutations correlated with lower (CTNNB1, NRAS, or IDH1) or higher (BRAF, TP53, or CASP8) leukocyte levels across all cancers. Multiple control modalities of the intracellular and extracellular networks (transcription, microRNAs, copy number, and epigenetic processes) were involved in tumor-immune cell interactions, both across and within immune subtypes. Our immunogenomics pipeline to characterize these heterogeneous tumors and the resulting data are intended to serve as a resource for future targeted studies to further advance the field.", 
"The definition and classification of chronic kidney disease (CKD) have evolved over time, but current international guidelines define this condition as decreased kidney function shown by glomerular filtration rate (GFR) of less than 60 mL/min per 1.73 m(2), or markers of kidney damage, or both, of at least 3 months duration, regardless of the underlying cause. Diabetes and hypertension are the main causes of CKD in all high-income and middle-income countries, and also in many low-income countries. Incidence, prevalence, and progression of CKD also vary within countries by ethnicity and social determinants of health, possibly through epigenetic influence. Many people are asymptomatic or have nonspecific symptoms such as lethargy, itch, or loss of appetite. Diagnosis is commonly made after chance findings from screening tests (urinary dipstick or blood tests), or when symptoms become severe. The best available indicator of overall kidney function is GFR, which is measured either via exogenous markers (eg, DTPA, iohexol), or estimated using equations. Presence of proteinuria is associated with increased risk of progression of CKD and death. Kidney biopsy samples can show definitive evidence of CKD, through common changes such as glomerular sclerosis, tubular atrophy, and interstitial fibrosis. Complications include anaemia due to reduced production of erythropoietin by the kidney; reduced red blood cell survival and iron deficiency; and mineral bone disease caused by disturbed vitamin D, calcium, and phosphate metabolism. People with CKD are five to ten times more likely to die prematurely than they are to progress to end stage kidney disease. This increased risk of death rises exponentially as kidney function worsens and is largely attributable to death from cardiovascular disease, although cancer incidence and mortality are also increased. Health-related quality of life is substantially lower for people with CKD than for the general population, and falls as GFR declines. Interventions targeting specific symptoms, or aimed at supporting educational or lifestyle considerations, make a positive difference to people living with CKD. Inequity in access to services for this disease disproportionally affects disadvantaged populations, and health service provision to incentivise early intervention over provision of care only for advanced CKD is still evolving in many countries.", 
"Pancreatic cancer is a major cause of cancer-associated mortality, with a dismal overall prognosis that has remained virtually unchanged for many decades. Currently, prevention or early diagnosis at a curable stage is exceedingly difficult; patients rarely exhibit symptoms and tumours do not display sensitive and specific markers to aid detection. Pancreatic cancers also have few prevalent genetic mutations; the most commonly mutated genes are KRAS, CDKN2A (encoding p16), TP53 and SMAD4 - none of which are currently druggable. Indeed, therapeutic options are limited and progress in drug development is impeded because most pancreatic cancers are complex at the genomic, epigenetic and metabolic levels, with multiple activated pathways and crosstalk evident. Furthermore, the multilayered interplay between neoplastic and stromal cells in the tumour microenvironment challenges medical treatment. Fewer than 20% of patients have surgically resectable disease; however, neoadjuvant therapies might shift tumours towards resectability. Although newer drug combinations and multimodal regimens in this setting, as well as the adjuvant setting, appreciably extend survival, similar to 80% of patients will relapse after surgery and ultimately die of their disease. Thus, consideration of quality of life and overall survival is important. In this Primer, we summarize the current understanding of the salient pathophysiological, molecular, translational and clinical aspects of this disease. In addition, we present an outline of potential future directions for pancreatic cancer research and patient management.", 
"An increasingly recognized resistance mechanism to androgen receptor (AR)-directed therapy in prostate cancer involves epithelial plasticity, in which tumor cells demonstrate low to absent AR expression and often have neuroendocrine features. The etiology and molecular basis for this 'alternative' treatment-resistant cell state remain incompletely understood. Here, by analyzing whole-exome sequencing data of metastatic biopsies from patients, we observed substantial genomic overlap between castration-resistant tumors that were histologically characterized as prostate adenocarcinomas (CRPC-Adeno) and neuroendocrine prostate cancer (CRPC-NE); analysis of biopsy samples from the same individuals over time points to a model most consistent with divergent clonal evolution. Genome-wide DNA methylation analysis revealed marked epigenetic differences between CRPC-NE tumors and CRPC-Adeno, and also designated samples of CRPC-Adeno with clinical features of AR independence as CRPC-NE, suggesting that epigenetic modifiers may play a role in the induction and/or maintenance of this treatment-resistant state. This study supports the emergence of an alternative, 'AR-indifferent' cell state through divergent clonal evolution as a mechanism of treatment resistance in advanced prostate cancer.", 
"Renal cell carcinoma (RCC) denotes cancer originated from the renal epithelium and accounts for >90% of cancers in the kidney. The disease encompasses >10 histological and molecular subtypes, of which clear cell RCC (ccRCC) is most common and accounts for most cancer-related deaths. Although somatic VHL mutations have been described for some time, more-recent cancer genomic studies have identified mutations in epigenetic regulatory genes and demonstrated marked intra-tumour heterogeneity, which could have prognostic, predictive and therapeutic relevance. Localized RCC can be successfully managed with surgery, whereas metastatic RCC is refractory to conventional chemotherapy. However, over the past decade, marked advances in the treatment of metastatic RCC have been made, with targeted agents including sorafenib, sunitinib, bevacizumab, pazopanib and axitinib, which inhibit vascular endothelial growth factor (VEGF) and its receptor (VEGFR), and everolimus and temsirolimus, which inhibit mechanistic target of rapamycin complex1 (mTORC1), being approved. Since 2015, agents with additional targets aside from VEGFR have been approved, such as cabozantinib and lenvatinib; immunotherapies, such as nivolumab, have also been added to the armamentarium for metastatic RCC. Here, we provide an overview of the biology of RCC, with a focus on ccRCC, as well as updates to complement the current clinical guidelines and an outline of potential future directions for RCC research and therapy.", 
"Suicide is a complex public health problem of global importance. Suicidal behaviour differs between sexes, age groups, geographic regions, and sociopolitical settings, and variably associates with different risk factors, suggesting aetiological heterogeneity. Although there is no effective algorithm to predict suicide in clinical practice, improved recognition and understanding of clinical, psychological, sociological, and biological factors might help the detection of high-risk individuals and assist in treatment selection. Psychotherapeutic, pharmacological, or neuromodulatory treatments of mental disorders can often prevent suicidal behaviour; additionally, regular follow-up of people who attempt suicide by mental health services is key to prevent future suicidal behaviour.", 
"Recent studies have suggested that the intestinal microbiome plays an important role in modulating risk of several chronic diseases, including inflammatory bowel disease, obesity, type 2 diabetes, cardiovascular disease, and cancer. At the same time, it is now understood that diet plays a significant role in shaping the microbiome, with experiments showing that dietary alterations can induce large, temporary microbial shifts within 24 h. Given this association, there may be significant therapeutic utility in altering microbial composition through diet. This review systematically evaluates current data regarding the effects of several common dietary components on intestinal microbiota. We show that consumption of particular types of food produces predictable shifts in existing host bacterial genera. Furthermore, the identity of these bacteria affects host immune and metabolic parameters, with broad implications for human health. Familiarity with these associations will be of tremendous use to the practitioner as well as the patient.", 
"BACKGROUND Diffuse large B-cell lymphomas (DLBCLs) are phenotypically and genetically heterogeneous. Gene-expression profiling has identified subgroups of DLBCL (activated B-cell-like [ABC], germinal-center B-cell-like [GCB], and unclassified) according to cell of origin that are associated with a differential response to chemotherapy and targeted agents. We sought to extend these findings by identifying genetic subtypes of DLBCL based on shared genomic abnormalities and to uncover therapeutic vulnerabilities based on tumor genetics. METHODS We studied 574 DLBCL biopsy samples using exome and transcriptome sequencing, array-based DNA copy-number analysis, and targeted amplicon resequencing of 372 genes to identify genes with recurrent aberrations. We developed and implemented an algorithm to discover genetic subtypes based on the co-occurrence of genetic alterations. RESULTS We identified four prominent genetic subtypes in DLBCL, termed MCD (based on the co-occurrence of MYD88(L265P) and CD79B mutations), BN2 (based on BCL6 fusions and NOTCH2 mutations), N1 (based on NOTCH1 mutations), and EZB (based on EZH2 mutations and BCL2 translocations). Genetic aberrations in multiple genes distinguished each genetic subtype from other DLBCLs. These subtypes differed phenotypically, as judged by differences in gene-expression signatures and responses to immunochemotherapy, with favorable survival in the BN2 and EZB subtypes and inferior outcomes in the MCD and N1 subtypes. Analysis of genetic pathways suggested that MCD and BN2 DLBCLs rely on chronic active B-cell receptor signaling that is amenable to therapeutic inhibition. CONCLUSIONS We uncovered genetic subtypes of DLBCL with distinct genotypic, epigenetic, and clinical characteristics, providing a potential nosology for precision-medicine strategies in DLBCL.", 
"The MYC oncogene encodes a transcription factor, MYC, whose broad effects make its precise oncogenic role enigmatically elusive. The evidence to date suggests that MYC triggers selective gene expression amplification to promote cell growth and proliferation. Through its targets, MYC coordinates nutrient acquisition to produce ATP and key cellular building blocks that increase cell mass and trigger DNA replication and cell division. In cancer, genetic and epigenetic derangements silence checkpoints and unleash MYC's cell growth-and proliferation-promoting metabolic activities. Unbridled growth in response to deregulated MYC expression creates dependence on MYC-driven metabolic pathways, such that reliance on specific metabolic enzymes provides novel targets for cancer therapy. Significance: MYC's expression and activity are tightly regulated in normal cells by multiple mechanisms, including a dependence upon growth factor stimulation and replete nutrient status. In cancer, genetic deregulation of MYC expression and loss of checkpoint components, such as TP53, permit MYC to drive malignant transformation. However, because of the reliance of MYC-driven cancers on specific metabolic pathways, synthetic lethal interactions between MYC overexpression and specific enzyme inhibitors provide novel cancer therapeutic opportunities. (C) 2015 AACR.", 
"Cancer growth and progression are associated with immune suppression. Cancer cells have the ability to activate different immune checkpoint pathways that harbor immunosuppressive functions. Monoclonal antibodies that target immune checkpoints provided an immense breakthrough in cancer therapeutics. Among the immune checkpoint inhibitors, PD-1/PD-L1 and CTLA-4 inhibitors showed promising therapeutic outcomes, and some have been approved for certain cancer treatments, while others are under clinical trials. Recent reports have shown that patients with various malignancies benefit from immune checkpoint inhibitor treatment. However, mainstream initiation of immune checkpoint therapy to treat cancers is obstructed by the low response rate and immune-related adverse events in some cancer patients. This has given rise to the need for developing sets of biomarkers that predict the response to immune checkpoint blockade and immune-related adverse events. In this review, we discuss different predictive biomarkers for anti-PD-1/PD-L1 and anti-CTLA-4 inhibitors, including immune cells, PD-L1 overexpression, neoantigens, and genetic and epigenetic signatures. Potential approaches for further developing highly reliable predictive biomarkers should facilitate patient selection for and decision-making related to immune checkpoint inhibitor-based therapies.", 
"The hippocampus provided the gateway into much of what we have learned about stress and brain structural and functional plasticity, and this initial focus has expanded to other interconnected brain regions, such as the amygdala and prefrontal cortex. Starting with the discovery of adrenal steroid, and later, estrogen receptors in the hippocampal formation, and subsequent discovery of dendritic and spine synapse remodeling and neurogenesis in the dentate gyrus, mechanistic studies have revealed both genomic and rapid non-genomic actions of circulating steroid hormones in the brain. Many of these actions occur epigenetically and result in ever-changing patterns of gene expression, in which there are important sex differences that need further exploration. Moreover, glucocorticoid and estrogen actions occur synergistically with an increasing number of cellular mediators that help determine the qualitative nature of the response. The hippocampus has also been a gateway to understanding lasting epigenetic effects of early-life experiences. These findings in animal models have resulted in translation to the human brain and have helped change thinking about the nature of brain malfunction in psychiatric disorders and during aging, as well as the mechanisms of the effects of early-life adversity on the brain and the body.", 
"EMT and MET comprise the processes by which cells transit between epithelial and mesenchymal states, and they play integral roles in both normal development and cancer metastasis. This article reviews these processes and the molecular pathways that contribute to them. First, we compare embryogenesis and development with cancer metastasis. We then discuss the signaling pathways and the differential expression and down-regulation of receptors in both tumor cells and stromal cells, which play a role in EMT and metastasis. We further delve into the clinical implications of EMT and MET in several types of tumors, and lastly, we discuss the role of epigenetic events that regulate EMT/MET processes. We hypothesize that reversible epigenetic events regulate both EMT and MET, and thus, also regulate the development of different types of metastatic cancers.", 
"This review provides general information to serve as a primer for those embarking on understanding food allergy and also details advances and updates in epidemiology, pathogenesis, diagnosis, and treatment that have occurred over the 4 years since our last comprehensive review. Although firm prevalence data are lacking, there is a strong impression that food allergy has increased, and rates as high as approximately 10% have been documented. Genetic, epigenetic, and environmental risk factors are being elucidated increasingly, creating potential for improved prevention and treatment strategies targeted to those at risk. Insights on pathophysiology reveal a complex interplay of the epithelial barrier, mucosal and systemic immune response, route of exposure, and microbiome among other influences resulting in allergy or tolerance. The diagnosis of food allergy is largely reliant on medical history, tests for sensitization, and oral food challenges, but emerging use of component-resolved diagnostics is improving diagnostic accuracy. Additional novel diagnostics, such as basophil activation tests, determination of epitope binding, DNA methylation signatures, and bioinformatics approaches, will further change the landscape. A number of prevention strategies are under investigation, but early introduction of peanut has been advised as a public health measure based on existing data. Management remains largely based on allergen avoidance, but a panoply of promising treatment strategies are in phase 2 and 3 studies, providing immense hope that better treatment will be imminently and widely available, whereas numerous additional promising treatments are in the preclinical and clinical pipeline.", 
"Macrophages are myeloid immune cells that are strategically positioned throughout the body tissues, where they ingest and degrade dead cells, debris, and foreign material and orchestrate inflammatory processes. Here we review two major recent paradigm shifts in our understanding of tissue macrophage biology. The first is the realization that most tissue-resident macrophages are established prenatally and maintained through adulthood by longevity and self-renewal. Their generation and maintenance are thus independent from ongoing hematopoiesis, although the cells can be complemented by adult monocyte-derived macrophages. Second, aside from being immune sentinels, tissue macrophages form integral components of their host tissue. This entails their specialization in response to local environmental cues to contribute to the development and specific function of their tissue of residence. Factors that govern tissue macrophage specialization are emerging. Moreover, tissue specialization is reflected in discrete gene expression profiles of macrophages, as well as epigenetic signatures reporting actual and potential enhancer usage.", 
"The discovery of long non-coding RNA (lncRNA) has dramatically altered our understanding of cancer. Here, we describe a comprehensive analysis of lncRNA alterations at transcriptional, genomic, and epigenetic levels in 5,037 human tumor specimens across 13 cancer types from The Cancer Genome Atlas. Our results suggest that the expression and dysregulation of lncRNAs are highly cancer type specific compared with protein- coding genes. Using the integrative data generated by this analysis, we present a clinically guided small interfering RNA screening strategy and a co-expression analysis approach to identify cancer driver lncRNAs and predict their functions. This provides a resource for investigating lncRNAs in cancer and lays the groundwork for the development of new diagnostics and treatments.", 
"Multidrug resistance (MDR) is a serious phenomenon employed by cancer cells which hampers the success of cancer pharmacotherapy. One of the common mechanisms of MDR is the overexpression of ATP-binding cassette (ABC) efflux transporters in cancer cells such as P-glycoprotein (P-gp/ABCB1), multidrug resistance-associated protein 2 (MRP2/ABCC2), and breast cancer resistance protein (BCRP/ABCG2) that limits the prolonged and effective use of chemotherapeutic drugs. Researchers have found that developing inhibitors of ABC efflux transporters as chemosensitizers could overcome MDR. But the clinical trials have shown that most of these chemosensitizers are merely toxic and only show limited or no benefits to cancer patients, thus new inhibitors are being explored. Recent findings also suggest that efflux pumps of the ABC transporter family are subject to epigenetic gene regulation. In this review, we summarize recent findings of the role of ABC efflux transporters in MDR. (C) 2015 Elsevier Ireland Ltd. All rights reserved.", 
"The mechanisms underlying human natural killer (NK) cell phenotypic and functional heterogeneity are unknown. Here, we describe the emergence of diverse subsets of human NK cells selectively lacking expression of signaling proteins after human cytomegalovirus (HCMV) infection. The absence of Band myeloid cell-related signaling protein expression in these NK cell subsets correlated with promoter DNA hypermethylation. Genome-wide DNA methylation patterns were strikingly similar between HCMV-associated adaptive NK cells and cytotoxic effector T cells but differed from those of canonical NK cells. Functional interrogation demonstrated altered cytokine responsiveness in adaptive NK cells that was linked to reduced expression of the transcription factor PLZF. Furthermore, subsets of adaptive NK cells demonstrated significantly reduced functional responses to activated autologous T cells. The present results uncover a spectrum of epigenetically unique adaptive NK cell subsets that diversify in response to viral infection and have distinct functional capabilities compared to canonical NK cell subsets.", 
"Cancer tissues are composed of cancer cells and the surrounding stromal cells (e.g., fibroblasts, vascular endothelial cells, and immune cells), in addition to the extracellular matrix. Most studies investigating carcinogenesis and the progression, invasion, metastasis, and angiogenesis of cancer have focused on alterations in cancer cells, including genetic and epigenetic changes. Recently, interactions between cancer cells and the stroma have attracted considerable attention, and increasing evidence has accumulated on this. Several researchers have gradually clarified the origins, features, and roles of cancer-associated fibroblasts (CAFs), a major component of the cancer stroma. CAFs function in a similar manner to myofibroblasts during wound healing. We previously reported the relationship between CAFs and angiogenesis. Interleukin-6 (IL-6), a multifunctional cytokine, plays a central role in regulating inflammatory and immune responses, and important roles in the progression, including proliferation, migration, and angiogenesis, of several cancers. We showed that CAFs are an important IL-6 source and that anti-IL-6 receptor antibody suppressed angiogenesis and inhibited tumor-stroma interactions. Furthermore, CAFs contribute to drug-resistance acquisition in cancer cells. The interaction between cancer cells and the stroma could be a potential target for anti-cancer therapy.", 
"The 'hallmarks of cancer' are generally accepted as a set of genetic and epigenetic alterations that a normal cell must accrue to transform into a fully malignant cancer. It follows that therapies designed to counter these alterations might be effective as anti-cancer strategies. Over the past 30 years, research on the BCL-2-regulated apoptotic pathway has led to the development of small-molecule compounds, known as 'BH3-mimetics', that bind to pro-survival BCL-2 proteins to directly activate apoptosis of malignant cells. This Timeline article focuses on the discovery and study of BCL-2, the wider BCL-2 protein family and, specifically, its roles in cancer development and therapy.", 
"The extent of tumor heterogeneity is an emerging theme that researchers are only beginning to understand. How genetic and epigenetic heterogeneity affects tumor evolution and clinical progression is unknown. The precise nature of the environmental factors that influence this heterogeneity is also yet to be characterized. Nature Medicine, Nature Biotechnology and the Volkswagen Foundation organized a meeting focused on identifying the obstacles that need to be overcome to advance translational research in and tumor heterogeneity. Once these key questions were established, the attendees devised potential solutions. Their ideas are presented here.", 
"Humans show strong sex differences in immunity to infection and autoimmunity, suggesting sex hormones modulate immune responses. Indeed, receptors for estrogens (ERs) regulate cells and pathways in the innate and adaptive immune system, as well as immune cell development. ERs are ligand-dependent transcription factors that mediate long-range chromatin interactions and form complexes at gene regulatory elements, thus promoting epigenetic changes and transcription. ERs also participate in membrane-initiated steroid signaling to generate rapid responses. Estradiol and ER activity show profound dose- and context-dependent effects on innate immune signaling pathways and myeloid cell development. While estradiol most often promotes the production of type I interferon, innate pathways leading to pro-inflammatory cytokine production may be enhanced or dampened by ER activity. Regulation of innate immune cells and signaling by ERs may contribute to the reported sex differences in innate immune pathways. Here we review the recent literature and highlight several molecular mechanisms by which ERs regulate the development or functional responses of innate immune cells. (C) 2015 Elsevier Inc. All rights reserved.", 
"Evasion of immune system is a hallmark of cancer, which enables cancer cells to escape the attack from immune cells. Cancer cells can express many immune inhibitory signalling proteins to cause immune cell dysfunction and apoptosis. One of these inhibitory molecules is programmed death-ligand-1 (PD-L1), which binds to programmed death-1 (PD-1) expressed on T-cells, B-cells, dendritic cells and natural killer T-cells to suppress anti-cancer immunity. Therefore, anti-PD-L1 and anti-PD-1 antibodies have been used for the treatment of cancer, showing promising outcomes. However, only a proportion of patients respond to the treatments. Further understanding of the regulation of PD-L1 expression could be helpful for the improvement of anti-PD-L1 and anti-PD-1 treatments. Studies have shown that PD-L1 expression is regulated by signalling pathways, transcriptional factors and epigenetic factors. In this review, we summarise the recent progress of the regulation of PD-L1 expression in cancer cells and propose a regulatory model for unified explanation. Both PI3K and MAPK pathways are involved in PD-L1 regulation but the downstream molecules that control PD-L1 and cell proliferation may differ. Transcriptional factors hypoxia-inducible factor-1 alpha and signal transducer and activation of transcription-3 act on the promoter of PD-L1 to regulate its expression. In addition, microRNAs including miR-570, miR-513, miR-197, miR-34a and miR-200 negatively regulate PD-L1. Clinically, it could increase treatment efficacy of targeted therapy by choosing those molecules that control both PD-L1 expression and cell proliferation.", 
"Excessive fat deposition in obesity has a multifactorial aetiology, but is widely considered the result of disequilibrium between energy intake and expenditure. Despite specific public health policies and individual treatment efforts to combat the obesity epidemic, >2 billion people worldwide are overweight or obese. The central nervous system circuitry, fuel turnover and metabolism as well as adipose tissue homeostasis are important to comprehend excessive weight gain and associated comorbidities. Obesity has a profound impact on quality of life, even in seemingly healthy individuals. Diet, physical activity or exercise and lifestyle changes are the cornerstones of obesity treatment, but medical treatment and bariatric surgery are becoming important. Family history, food environment, cultural preferences, adverse reactions to food, perinatal nutrition, previous or current diseases and physical activity patterns are relevant aspects for the health care professional to consider when treating the individual with obesity. Clinicians and other health care professionals are often ill-equipped to address the important environmental and socioeconomic drivers of the current obesity epidemic. Finally, understanding the epigenetic and genetic factors as well as metabolic pathways that take advantage of 'omics' technologies could play a very relevant part in combating obesity within a precision approach.", 
"Macrophages have protective roles in immunity to pathogens, tissue development, homeostasis and repair following damage. Maladaptive immunity and inflammation provoke changes in macrophage function that are causative of disease. Despite a historical wealth of knowledge about macrophages, recent advances have revealed unknown aspects of their development and function. Following development, macrophages are activated by diverse signals. Such tissue microenvironmental signals together with epigenetic changes influence macrophage development, activation and functional diversity, with consequences in disease and homeostasis. We discuss here how recent discoveries in these areas have led to a multidimensional concept of macrophage ontogeny, activation and function. In connection with this, we also discuss how technical advances facilitate a new roadmap for the isolation and analysis of macrophages at high resolution.", 
"Progressive liver fibrosis, induced by chronic viral and metabolic disorders, leads to more than one million deaths annually via development of cirrhosis, although no antifibrotic therapy has been approved to date. Transdifferentiation (or activation) of hepatic stellate cells is the major cellular source of matrix protein-secreting myofibroblasts, the major driver of liver fibrogenesis. Paracrine signals from injured epithelial cells, fibrotic tissue microenvironment, immune and systemic metabolic dysregulation, enteric dysbiosis, and hepatitis viral products can directly or indirectly induce stellate cell activation. Dysregulated intracellular signaling, epigenetic changes, and cellular stress response represent candidate targets to deactivate stellate cells by inducing reversion to inactivated state, cellular senescence, apoptosis, and/or clearance by immune cells. Cell type- and target-specific pharmacological intervention to therapeutically induce the deactivation will enable more effective and less toxic precision antifibrotic therapies. (C) 2017 Elsevier B.V. All rights reserved.", 
"In recent years, there has been a tremendous and growing interest among researchers to investigate the role of mircoRNA (miRNA) in normal cellular as well as in disease processes. miRNAs are a family of small non-coding RNAs which were reported to regulate the expression of various oncogenes or tumor suppressor genes. The expression profiling of miRNAs has already entered into cancer clinics as diagnostic and prognostic biomarkers to assess tumor initiation, progression and response to treatment in cancer patients. This review summarizes: (i) the current understanding of interactions between miRNAs and their target genes, (ii) recent advances in the regulatory mechanisms that control the expression of genes related to carcinogenesis, and (iii) the role of miRNAs in cancer diagnosis and therapy.", 
"Irritable bowel syndrome (IBS) is a functional gastrointestinal disease with a high population prevalence. The disorder can be debilitating in some patients, whereas others may have mild or moderate symptoms. The most important single risk factors are female sex, younger age and preceding gastrointestinal infections. Clinical symptoms of IBS include abdominal pain or discomfort, stool irregularities and bloating, as well as other somatic, visceral and psychiatric comorbidities. Currently, the diagnosis of IBS is based on symptoms and the exclusion of other organic diseases, and therapy includes drug treatment of the predominant symptoms, nutrition and psychotherapy. Although the underlying pathogenesis is far from understood, aetiological factors include increased epithelial hyperpermeability, dysbiosis, inflammation, visceral hypersensitivity, epigenetics and genetics, and altered brain-gut interactions. IBS considerably affects quality of life and imposes a profound burden on patients, physicians and the health-care system. The past decade has seen remarkable progress in our understanding of functional bowel disorders such as IBS that will be summarized in this Primer.", 
"Approximately 50% of epithelial ovarian cancers (EOC) exhibit defective DNA repair via homologous recombination (HR) due to genetic and epigenetic alterations of HR pathway genes. Defective HR is an important therapeutic target in EOC as exemplified by the efficacy of platinum analogues in this disease, as well as the advent of PARP inhibitors, which exhibit synthetic lethality when applied to HR-deficient cells. Here, we describe the genotypic and phenotypic characteristics of HR-deficient EOCs, discuss current and emerging approaches for targeting these tumors, and present challenges associated with these approaches, focusing on development and overcoming resistance. Significance: Defective DNA repair via HR is a pivotal vulnerability of EOC, particularly of the high-grade serous histologic subtype. Targeting defective HR offers the unique opportunity of exploiting molecular differences between tumor and normal cells, thereby inducing cancer-specific synthetic lethality; the promise and challenges of these approaches in ovarian cancer are discussed in this review. (C)2015 AACR.", 
"Anticancer drugs resistance is a complex process that arises from altering in the drug targets. Advances in the DNA microarray, proteomics technology and the development of targeted therapies provide the new strategies to overcome the drug resistance. Although a design of the new chemotherapy agents is growing quickly, effective chemotherapy agent has not been discovered against the advanced stage of cancer (such as invasion and metastasis). The cancer cell resistance against the anticancer agents can be due to many factors such as the individual's genetic differences, especially in tumoral somatic cells. Also, the cancer drug resistance is acquired, the drug resistance can be occurred by different mechanisms, including multi-drug resistance, cell death inhibiting (apoptosis suppression), altering in the drug metabolism, epigenetic and drug targets, enhancing DNA repair and gene amplification. In this review, we outlined the mechanisms of cancer drug resistance and in following, the treatment failures by common chemotherapy agents in the different type of cancers.", 
"The endothelins comprise three structurally similar 21-amino acid peptides. Endothelin-1 and -2 activate two G-protein coupled receptors, ETA and ETB, with equal affinity, whereas endothelin-3 has a lower affinity for the ETA subtype. Genes encoding the peptides are present only among vertebrates. The ligand-receptor signaling pathway is a vertebrate innovation and may reflect the evolution of endothelin-1 as the most potent vasoconstrictor in the human cardiovascular system with remarkably long lasting action. Highly selective peptide ETA and ETB antagonists and ETB agonists together with radiolabeled analogs have accurately delineated endothelin pharmacology in humans and animal models, although surprisingly no ETA agonist has been discovered. ET antagonists (bosentan, ambrisentan) have revolutionized the treatment of pulmonary arterial hypertension, with the next generation of antagonists exhibiting improved efficacy (macitentan). Clinical trials continue to explore new applications, particularly in renal failure and for reducing proteinuria in diabetic nephropathy. Translational studies suggest a potential benefit of ETB agonists in chemotherapy and neuroprotection. However, demonstrating clinical efficacy of combined inhibitors of the endothelin converting enzyme and neutral endopeptidase has proved elusive. Over 28 genetic modifications have been made to the ET system in mice through global or cell-specific knockouts, knock ins, or alterations in gene expression of endothelin ligands or their target receptors. These studies have identified key roles for the endothelin isoforms and new therapeutic targets in development, fluid-electrolyte homeostasis, and cardiovascular and neuronal function. For the future, novel pharmacological strategies are emerging via small molecule epigenetic modulators, biologicals such as ETB monoclonal antibodies and the potential of signaling pathway biased agonists and antagonists.", 
"Exhausted CD8 T (Tex) cells are a distinct cell lineage that arise during chronic infections and cancers in animal models and humans. Tex cells are characterized by progressive loss of effector functions, high and sustained inhibitory receptor expression, metabolic dysregulation, poor memory recall and homeostatic self-renewal, and distinct transcriptional and epigenetic programs. The ability to reinvigorate Tex cells through inhibitory receptor blockade, such as alpha PD-1, highlights the therapeutic potential of targeting this population. Emerging insights into the mechanisms of exhaustion are informing immunotherapies for cancer and chronic infections. However, like other immune cells, Tex cells are heterogeneous and include progenitor and terminal subsets with unique characteristics and responses to checkpoint blockade. Here, we review our current understanding of Tex cell biology, including the developmental paths, transcriptional and epigenetic features, and cell intrinsic and extrinsic factors contributing to exhaustion and how this knowledge may inform therapeutic targeting of Tex cells in chronic infections, autoimmunity, and cancer.", 
"It is now well established that the immune system can recognize developing cancers and that therapeutic manipulation of immunity can induce tumor regression. The capacity to manifest remarkably durable responses in some patients has been ascribed in part to T cells that can (a) kill tumor cells directly, (b) orchestrate diverse antitumor immune responses, (c) manifest long-lasting memory, and (d) display remarkable specificity for tumor-derived proteins. This specificity stems from fundamental differences between cancer cells and their normal counterparts in that the former develop protein-altering mutations and undergo epigenetic and genetic alterations, resulting in aberrant protein expression. These events can result in formation of tumor antigens. The identification of mutated and aberrantly expressed self-tumor antigens has historically been time consuming and laborious. While mutant antigens are usually expressed in a tumor-specific manner, aberrantly expressed antigens are often shared between cancers and, therefore, in the past, have been the major focus of therapeutic cancer vaccines. However, advances in next-generation sequencing and epitope prediction now permit the rapid identification of mutant tumor neoantigens. This review focuses on a discussion of mutant tumor neoantigens and their use in personalizing cancer immunotherapies.", 
"Advances in single-cell RNA sequencing (scRNA-seq) have allowed for comprehensive analysis of the immune system. In this Review, we briefly describe the available scRNA-seq technologies together with their corresponding strengths and weaknesses. We discuss in depth how scRNA-seq can be used to deconvolve immune system heterogeneity by identifying novel distinct immune cell subsets in health and disease, characterizing stochastic heterogeneity within a cell population and building developmental 'trajectories' for immune cells. Finally, we discuss future directions of the field and present integrated approaches to complement molecular information from a single cell with studies of the environment, epigenetic state and cell lineage.", 
"Long-lived memory-like'' NK cells have been identified in individuals infected by human cytomegalovirus (HCMV), but little is known about how the memory-like NK cell pool is formed. Here, we have shown that HCMV-infected individuals have several distinct subsets of memory-like NK cells that are often deficient for multiple transcription factors and signaling proteins, including tyrosine kinase SYK, for which the reduced expression was stable over time and correlated with epigenetic modification of the gene promoter. Deficient expression of these proteins was largely confined to the recently discovered FcRg-deficient NK cells that display enhanced antibody-dependent functional activity. Importantly, FcRg-deficient NK cells exhibited robust preferential expansion in response to virus-infected cells (both HCMV and influenza) in an antibody-dependent manner. These findings suggest that the memory-like NK cell pool is shaped and maintained by a mechanism that involves both epigenetic modification of gene expression and antibody-dependent expansion.", 
"Extensive research over the past half a century indicates that reactive oxygen species (ROS) play an important role in cancer. Although low levels of ROS can be beneficial, excessive accumulation can promote cancer. One characteristic of cancer cells that distinguishes them from normal cells is their ability to produce increased numbers of ROS and their increased dependence on an antioxidant defense system. ROS are produced as a byproduct intracellularly by mitochondria and other cellular elements and exogenously by pollutants, tobacco, smoke, drugs, xenobiotics, and radiation. ROS modulate various cell signaling pathways, which are primarily mediated through the transcription factors NF-kappa B and STAT3, hypoxia-inducible factor-1 alpha, kinases, growth factors, cytokines and other proteins, and enzymes; these pathways have been linked to cellular transformation, inflammation, tumor survival, proliferation, invasion, angiogenesis, and metastasis of cancer. ROS are also associated with epigenetic changes in genes, which is helpful in diagnosing diseases. This review considers the role of ROS in the various stages of cancer development. Finally, we provide evidence that nutraceuticals derived from Mother Nature are highly effective in eliminating cancer cells. (C) 2016 Elsevier Ireland Ltd. All rights reserved.", 
"There are few in vitro models of exocrine pancreas development and primary human pancreatic adenocarcinoma (PDAC). We establish three-dimensional culture conditions to induce the differentiation of human pluripotent stem cells into exocrine progenitor organoids that form ductal and acinar structures in culture and in vivo. Expression of mutant KRAS or TP53 in progenitor organoids induces mutation-specific phenotypes in culture and in vivo. Expression of TP53(R175H) induces cytosolic SOX9 localization. In patient tumors bearing TP53 mutations, SOX9 was cytoplasmic and associated with mortality. We also define culture conditions for clonal generation of tumor organoids from freshly resected PDAC. Tumor organoids maintain the differentiation status, histoarchitecture and phenotypic heterogeneity of the primary tumor and retain patient-specific physiological changes, including hypoxia, oxygen consumption, epigenetic marks and differences in sensitivity to inhibition of the histone methyltransferase EZH2. Thus, pancreatic progenitor organoids and tumor organoids can be used to model PDAC and fat drug screening to identify precision therapy strategies.", 
"Arsenic (As) is ubiquitous in nature and humans being exposed to arsenic via atmospheric air, ground water and food sources are certain. Major sources of arsenic contamination could be either through geological or via anthropogenic activities. In physiological individuals, organ system is described as group of organs that transact collectively and associate with other systems for conventional body functions. Arsenic has been associated with persuading a variety of complications in body organ systems: integumentary, nervous, respiratory, cardiovascular, hematopoietic, immune, endocrine, hepatic, renal, reproductive system and development. In this review, we outline the effects of arsenic on the human body with a main focus on assorted organ systems with respective disease conditions. Additionally, underlying mechanisms of disease development in each organ system due to arsenic have also been explored. Strikingly, arsenic has been able to induce epigenetic changes (in utero) and genetic mutations (a leading cause of cancer) in the body. Occurrence of various arsenic induced health effects involving emerging areas such as epigenetics and cancer along with their respective mechanisms are also briefly discussed. (C) 2015 Elsevier B.V. All rights reserved.", 
"Parental environmental factors, including diet, body composition, metabolism, and stress, affect the health and chronic disease risk of people throughout their lives, as captured in the Developmental Origins of Health and Disease concept. Research across the epidemiological, clinical, and basic science fields has identified the period around conception as being crucial for the processes mediating parental influences on the health of the next generation. During this time, from the maturation of gametes through to early embryonic development, parental lifestyle can adversely influence long-term risks of offspring cardiovascular, metabolic, immune, and neurological morbidities, often termed developmental programming. We review periconceptional induction of disease risk from four broad exposures: maternal overnutrition and obesity; maternal undernutrition; related paternal factors; and the use of assisted reproductive treatment. Studies in both humans and animal models have demonstrated the underlying biological mechanisms, including epigenetic, cellular, physiological, and metabolic processes. We also present a meta-analysis of mouse paternal and maternal protein undernutrition that suggests distinct parental periconceptional contributions to postnatal outcomes. We propose that the evidence for periconceptional effects on lifetime health is now so compelling that it calls for new guidance on parental preparation for pregnancy, beginning before conception, to protect the health of offspring.", 
"Long non-coding RNAs (lncRNAs) refer to a group of RNAs that are usually more than 200 nucleotides and are not involved in protein generation. Instead, lncRNAs are involved in different regulatory processes, such as regulation of gene expression. Different lncRNAs exist throughout the genome. LncRNAs are also known for their roles in different human diseases such as cancer. HOTAIR is an lncRNA that plays a role as an oncogenic molecule in different cancer cells, such as breast, gastric, colorectal, and cervical cancer cells. Therefore, HOTAIR expression level is a potential biomarker for diagnostic and therapeutic purposes in several cancers. This RNA takes part in epigenetic regulation of genes and plays an important role in different cellular pathways by interacting with Polycomb Repressive Complex 2 (PRC2). In this review, we describe the molecular function and regulation of HOTAIR and its role in different types of cancers.", 
"Mutant isocitrate dehydrogenase (IDH) 1 and 2 proteins alter the epigenetic landscape in acute myeloid leukemia (AML) cells through production of the oncometabolite (R)-2-hydroxyglutarate (2-HG). Here we performed a large-scale RNA interference (RNAi) screen to identify genes that are synthetic lethal to the IDH1(R132H) mutation in AML and identified the anti-apoptotic gene BCL-2. IDH1- and IDH2-mutant primary human AML cells were more sensitive than IDH1/2 wildtype cells to ABT-199, a highly specific BCL-2 inhibitor that is currently in clinical trials for hematologic malignancies, both ex vivo and in xenotransplant models. This sensitization effect was induced by (R)-2-HG-mediated inhibition of the activity of cytochrome c oxidase (COX) in the mitochondrial electron transport chain (ETC); suppression of COX activity lowered the mitochondrial threshold to trigger apoptosis upon BCL-2 inhibition. Our findings indicate that IDH1/2 mutation status may identify patients that are likely to respond to pharmacologic BCL-2 inhibition and form the rational basis for combining agents that disrupt ETC activity with ABT-199 in future clinical studies.", 
"T cell dysfunction is a hallmark of many cancers, but the basis for T cell dysfunction and the mechanisms by which antibody blockade of the inhibitory receptor PD-1 (anti-PD-1) reinvigorates T cells are not fully understood. Here we show that such therapy acts on a specific subpopulation of exhausted CD8(+) tumor-infiltrating lymphocytes (TILs). Dysfunctional CD8(+) TILs possess canonical epigenetic and transcriptional features of exhaustion that mirror those seen in chronic viral infection. Exhausted CD8(+) TILs include a subpopulation of 'progenitor exhausted' cells that retain polyfunctionality, persist long term and differentiate into 'terminally exhausted' TILs. Consequently, progenitor exhausted CD8(+) TILs are better able to control tumor growth than are terminally exhausted T cells. Progenitor exhausted TILs can respond to anti-PD-1 therapy, but terminally exhausted TILs cannot. Patients with melanoma who have a higher percentage of progenitor exhausted cells experience a longer duration of response to checkpoint-blockade therapy. Thus, approaches to expand the population of progenitor exhausted CD8(+) T cells might be an important component of improving the response to checkpoint blockade.", 
"Apoptosis or programmed cell death is natural way of removing aged cells from the body. Most of the anticancer therapies trigger apoptosis induction and related cell death networks to eliminate malignant cells. However, in cancer, de-regulated apoptotic signaling, particularly the activation of an anti-apoptotic systems, allows cancer cells to escape this program leading to uncontrolled proliferation resulting in tumor survival, therapeutic resistance and recurrence of cancer. This resistance is a complicated phenomenon that emanates from the interactions of various molecules and signaling pathways. In this comprehensive review we discuss the various factors contributing to apoptosis resistance in cancers. The key resistance targets that are discussed include (1) BcI-2 and Mcl-1 proteins; (2) autophagy processes; (3) necrosis and necroptosis; (4) heat shock protein signaling; (5) the proteasome pathway; (6) epigenetic mechanisms; and (7) aberrant nuclear export signaling. The shortcomings of current therapeutic modalities are highlighted and a broad spectrum strategy using approaches including (a) gossypol; (b) epigallocatechin-3-gallate; (c) UMI-77 (d) triptolide and (e) selinexor that can be used to overcome cell death resistance is presented. This review provides a roadmap for the design of successful anti-cancer strategies that overcome resistance to apoptosis for better therapeutic outcome in patients with cancer. (C) 2015 Elsevier Ltd.", 
"Epigenetic dysregulation has emerged as an important mechanism in cancer. Alterations in epigenetic machinery have become a major focus for targeted therapies. The current report describes the discovery and biological activity of a cyclopropylamine containing inhibitor of Lysine Demethylase 1 (LSD1), GSK2879552. This small molecule is a potent, selective, orally bioavailable, mechanism-based irreversible inactivator of LSD1. A proliferation screen of cell lines representing a number of tumor types indicated that small cell lung carcinoma (SCLC) is sensitive to LSD1 inhibition. The subset of SCLC lines and primary samples that undergo growth inhibition in response to GSK2879552 exhibit DNA hypomethylation of a signature set of probes, suggesting this may be used as a predictive biomarker of activity.", 
"Over the last several decades, it has become clear that epigenetic abnormalities may be one of the hallmarks of cancer. Posttranslational modifications of histones, for example, may play a crucial role in cancer development and progression by modulating gene transcription, chromatin remodeling, and nuclear architecture. Histone acetylation, a well-studied post-translational histone modification, is controlled by the opposing activities of histone acetyl-transferases (HATs) and histone deacetylases (HDACs). By removing acetyl groups, HDACs reverse chromatin acetylation and alter transcription of oncogenes and tumor suppressor genes. In addition, HDACs deacetylate numerous nonhistone cellular substrates that govern a wide array of biological processes including cancer initiation and progression. This review will discuss the role of HDACs in cancer and the therapeutic potential of HDAC inhibitors (HDACi) as emerging drugs in cancer treatment.", 
"Histone modifications are key epigenetic regulatory features that have important roles in many cellular events. Lysine methylations mark various sites on the tail and globular domains of histones and their levels are precisely balanced by the action of methyltransferases ('writers') and demethylases ('erasers'). In addition, distinct effector proteins ('readers') recognize specific methyl-lysines in a manner that depends on the neighboring amino-acid sequence and methylation state. Misregulation of histone lysine methylation has been implicated in several cancers and developmental defects. Therefore, histone lysine methylation has been considered a potential therapeutic target, and clinical trials of several inhibitors of this process have shown promising results. A more detailed understanding of histone lysine methylation is necessary for elucidating complex biological processes and, ultimately, for developing and improving disease treatments. This review summarizes enzymes responsible for histone lysine methylation and demethylation and how histone lysine methylation contributes to various biological processes.", 
"DNA methylation is known to be abnormal in all forms of cancer, but it is not really understood how this occurs and what is its role in tumorigenesis. In this review, we take a wide view of this problem by analyzing the strategies involved in setting up normal DNA methylation patterns and understanding how this stable epigenetic mark works to prevent gene activation during development. Aberrant DNA methylation in cancer can be generated either prior to or following cell transformation through mutations. Increasing evidence suggests, however, that most methylation changes are generated in a programmed manner and occur in a subpopulation of tissue cells during normal aging, probably predisposing them for tumorigenesis. It is likely that this methylation contributes to the tumor state by inhibiting the plasticity of cell differentiation processes. (C) 2016 AACR.", 
"Cancer is driven by genetic and epigenetic alterations that allow cells to overproliferate and escape mechanisms that normally control their survival and migration. Many of these alterations map to signaling pathways that control cell growth and division, cell death, cell fate, and cell motility, and can be placed in the context of distortions of wider signaling networks that fuel cancer progression, such as changes in the tumor microenvironment, angiogenesis, and inflammation. Mutations that convert cellular proto-oncogenes to oncogenes can cause hyper-activation of these signaling pathways, whereas inactivation of tumor suppressors eliminates critical negative regulators of signaling. An examination of the PI3K-Akt and Ras-ERK pathways illustrates how such alterations dysregulate signaling in cancer and produce many of the characteristic features of tumor cells.", 
"Macrophages are immune cells of haematopoietic origin that provide crucial innate immune defence and have tissue-specific functions in the regulation and maintenance of organ homeostasis. Recent studies of macrophage ontogeny, as well as transcriptional and epigenetic identity, have started to reveal the decisive role of the tissue stroma in the regulation of macrophage function. These findings suggest that most macrophages seed the tissues during embryonic development and functionally specialize in response to cytokines and metabolites that are released by the stroma and drive the expression of unique transcription factors. In this Review, we discuss how recent insights into macrophage ontogeny and macrophage stroma interactions contribute to our understanding of the crosstalk that shapes macrophage function and the maintenance of organ integrity.", 
"Diversity and plasticity are hallmarks of cells of the monocyte-macrophage lineage. In response to IFNs, Toll-like receptor engagement, or IL-4/IL-13 signaling, macrophages undergo M1 (classical) or M2 (alternative) activation, which represent extremes of a continuum in a universe of activation states. Progress has now been made in defining the signaling pathways, transcriptional networks, and epigenetic mechanisms underlying M1-M2 or M2-like polarized activation. Functional skewing of mononuclear phagocytes occurs in vivo under physiological conditions (e.g., ontogenesis and pregnancy) and in pathology (allergic and chronic inflammation, tissue repair, infection, and cancer). However, in selected preclinical and clinical conditions, coexistence of cells in different activation states and unique or mixed phenotypes have been observed, a reflection of dynamic changes and complex tissue-derived signals. The identification of mechanisms and molecules associated with macrophage plasticity and polarized activation provides a basis for macrophage-centered diagnostic and therapeutic strategies.", 
"BACKGROUND Many mutations that contribute to the pathogenesis of acute myeloid leukemia (AML) are undefined. The relationships between patterns of mutations and epigenetic phenotypes are not yet clear. METHODS We analyzed the genomes of 200 clinically annotated adult cases of de novo AML, using either whole-genome sequencing (50 cases) or whole-exome sequencing (150 cases), along with RNA and microRNA sequencing and DNA-methylation analysis. RESULTS AML genomes have fewer mutations than most other adult cancers, with an average of only 13 mutations found in genes. Of these, an average of 5 are in genes that are recurrently mutated in AML. A total of 23 genes were significantly mutated, and another 237 were mutated in two or more samples. Nearly all samples had at least 1 nonsynonymous mutation in one of nine categories of genes that are almost certainly relevant for pathogenesis, including transcription-factor fusions (18% of cases), the gene encoding nucleophosmin (NPM1) (27%), tumor-suppressor genes (16%), DNA-methylation-related genes (44%), signaling genes (59%), chromatin-modifying genes (30%), myeloid transcription-factor genes (22%), cohesin-complex genes (13%), and spliceosome-complex genes (14%). Patterns of cooperation and mutual exclusivity suggested strong biologic relationships among several of the genes and categories. CONCLUSIONS We identified at least one potential driver mutation in nearly all AML samples and found that a complex interplay of genetic events contributes to AML pathogenesis in individual patients. The databases from this study are widely available to serve as a foundation for further investigations of AML pathogenesis, classification, and risk stratification.", 
"CD4 T cells play critical roles in mediating adaptive immunity to a variety of pathogens. They are also involved in autoimmunity, asthma, and allergic responses as well as in tumor immunity. During TCR activation in a particular cytokine milieu, naive CD4 T cells may differentiate into one of several lineages of T helper (Th) cells, including Th1, Th2, Th17, and iTreg, as defined by their pattern of cytokine production and function. In this review, we summarize the discovery, functions, and relationships among Th cells; the cytokine and signaling requirements for their development; the networks of transcription factors involved in their differentiation; the epigenetic regulation of their key cytokines and transcription factors; and human diseases involving defective CD4 T cell differentiation.", 
"The past decade has highlighted the central role of epigenetic processes in cancer causation, progression and treatment. Next-generation sequencing is providing a window for visualizing the human epigenome and how it is altered in cancer. This view provides many surprises, including linking epigenetic abnormalities to mutations in genes that control DNA methylation, the packaging and the function of DNA in chromatin, and metabolism. Epigenetic alterations are leading candidates for the development of specific markers for cancer detection, diagnosis and prognosis. The enzymatic processes that control the epigenome present new opportunities for deriving therapeutic strategies designed to reverse transcriptional abnormalities that are inherent to the cancer epigenome.", 
"Cancer-associated IDH mutations are characterized by neomorphic enzyme activity and resultant 2-hydroxyglutarate (2HG) production. Mutational and epigenetic profiling of a large acute myeloid leukemia (AML) patient cohort revealed that IDH1/2-mutant AMLs display global DNA hypermethylation and a specific hypermethylation signature. Furthermore, expression of 2HG-producing IDH alleles in cells induced global DNA hypermethylation. In the AML cohort, IDH1/2 mutations were mutually exclusive with mutations in the alpha-ketoglutarate-dependent enzyme TET2, and TET2 loss-of-function mutations were associated with similar epigenetic defects as IDH1/2 mutants. Consistent with these genetic and epigenetic data, expression of IDH mutants impaired TET2 catalytic function in cells. Finally, either expression of mutant IDH1/2 or Tet2 depletion impaired hematopoietic differentiation and increased stem/progenitor cell marker expression, suggesting a shared proleukemogenic effect.", 
"Interleukin-10 (IL-10), a cytokine with anti-inflammatory properties, has a central role in infection by limiting the immune response to pathogens and thereby preventing damage to the host. Recently, an increasing interest in how IL10 expression is regulated in different immune cells has revealed some of the molecular mechanisms involved at the levels of signal transduction, epigenetics, transcription factor binding and gene activation. Understanding the specific molecular events that regulate the production of IL-10 will help to answer the remaining questions that are important for the design of new strategies of immune intervention.", 
"Epigenetic mechanisms are essential for normal development and maintenance of tissue-specific gene expression patterns in mammals. Disruption of epigenetic processes can lead to altered gene function and malignant cellular transformation. Global changes in the epigenetic landscape are a hallmark of cancer. The initiation and progression of cancer, traditionally seen as a genetic disease, is now realized to involve epigenetic abnormalities along with genetic alterations. Recent advancements in the rapidly evolving field of cancer epigenetics have shown extensive reprogramming of every component of the epigenetic machinery in cancer including DNA methylation, histone modifications, nucleosome positioning and non-coding RNAs, specifically microRNA expression. The reversible nature of epigenetic aberrations has led to the emergence of the promising field of epigenetic therapy, which is already making progress with the recent FDA approval of three epigenetic drugs for cancer treatment. In this review, we discuss the current understanding of alterations in the epigenetic landscape that occur in cancer compared with normal cells, the roles of these changes in cancer initiation and progression, including the cancer stem cell model, and the potential use of this knowledge in designing more effective treatment strategies.", 
"Background Cancers arise from multiple acquired mutations, which presumably occur over many years. Early stages in cancer development might be present years before cancers become clinically apparent. Methods We analyzed data from whole-exome sequencing of DNA in peripheral-blood cells from 12,380 persons, unselected for cancer or hematologic phenotypes. We identified somatic mutations on the basis of unusual allelic fractions. We used data from Swedish national patient registers to follow health outcomes for 2 to 7 years after DNA sampling. Results Clonal hematopoiesis with somatic mutations was observed in 10% of persons older than 65 years of age but in only 1% of those younger than 50 years of age. Detectable clonal expansions most frequently involved somatic mutations in three genes (DNMT3A, ASXL1, and TET2) that have previously been implicated in hematologic cancers. Clonal hematopoiesis was a strong risk factor for subsequent hematologic cancer (hazard ratio, 12.9; 95% confidence interval, 5.8 to 28.7). Approximately 42% of hematologic cancers in this cohort arose in persons who had clonality at the time of DNA sampling, more than 6 months before a first diagnosis of cancer. Analysis of bone marrow-biopsy specimens obtained from two patients at the time of diagnosis of acute myeloid leukemia revealed that their cancers arose from the earlier clones. Conclusions Clonal hematopoiesis with somatic mutations is readily detected by means of DNA sequencing, is increasingly common as people age, and is associated with increased risks of hematologic cancer and death. A subset of the genes that are mutated in patients with myeloid cancers is frequently mutated in apparently healthy persons; these mutations may represent characteristic early events in the development of hematologic cancers.", 
"Type I interferons (IFNs) activate intracellular antimicrobial programmes and influence the development of innate and adaptive immune responses. Canonical type I IFN signalling activates the Janus kinase (JAK)-signal transducer and activator of transcription (STAT) pathway, leading to transcription of IFN-stimulated genes (ISGs). Host, pathogen and environmental factors regulate the responses of cells to this signalling pathway and thus calibrate host defences while limiting tissue damage and preventing autoimmunity. Here, we summarize the signalling and epigenetic mechanisms that regulate type I IFN-induced STAT activation and ISG transcription and translation. These regulatory mechanisms determine the biological outcomes of type I IFN responses and whether pathogens are cleared effectively or chronic infection or autoimmune disease ensues.", 
"Populations of tumour cells display remarkable variability in almost every discernable phenotypic trait, including clinically important phenotypes such as ability to seed metastases and to survive therapy. This phenotypic diversity results from the integration of both genetic and non-genetic influences. Recent technological advances have improved the molecular understanding of cancers and the identification of targets for therapeutic interventions. However, it has become exceedingly apparent that the utility of profiles based on the analysis of tumours en masse is limited by intra-tumour genetic and epigenetic heterogeneity, as characteristics of the most abundant cell type might not necessarily predict the properties of mixed populations. In this Review, we discuss both genetic and non-genetic causes of phenotypic heterogeneity of tumour cells, with an emphasis on heritable phenotypes that serve as a substrate for clonal selection. We discuss the implications of intra-tumour heterogeneity in diagnostics and the development of therapeutic resistance.", 
"The Janus kinases (JAKs) and signal transducer and activator of transcription (STAT) proteins, particularly STAT3, are among the most promising new targets for cancer therapy. In addition to interleukin-6 (IL-6) and its family members, multiple pathways, including G-protein-coupled receptors (GPCRs), Toll-like receptors (TLRs) and microRNAs were recently identified to regulate JAK-STAT signalling in cancer. Well known for its role in tumour cell proliferation, survival, invasion and immunosuppression, JAK-STAT3 signalling also promotes cancer through inflammation, obesity, stem cells and the pre-metastatic niche. In addition to its established role as a transcription factor in cancer, STAT3 regulates mitochondrion functions, as well as gene expression through epigenetic mechanisms. Newly identified regulators and functions of JAK-STAT3 in tumours are important targets for potential therapeutic strategies in the treatment of cancer.", 
"Idiopathic pulmonary fibrosis is a devastating, age-related lung disease of unknown cause that has few treatment options. This disease was once thought to be a chronic inflammatory process, but current evidence indicates that the fibrotic response is driven by abnormally activated alveolar epithelial cells (AECs). These cells produce mediators that induce the formation of fibroblast and myofibroblast foci through the proliferation of resident mesenchymal cells, attraction of circulating fibrocytes, and stimulation of the epithelial to mesenchymal transition. The fibroblast and myofibroblast foci secrete excessive amounts of extracellular matrix, mainly collagens, resulting in scarring and destruction of the lung architecture. The mechanisms that link idiopathic pulmonary fibrosis with ageing and aberrant epithelial activation are unknown; evidence suggests that the abnormal recapitulation of developmental pathways and epigenetic changes have a role. In this Seminar, we review recent data on the clinical course, therapeutic options, and underlying mechanisms thought to be involved in the pathogenesis of idiopathic pulmonary fibrosis.", 
"Glioblastoma (GBM) is a brain tumor that carries a dismal prognosis and displays considerable heterogeneity. We have recently identified recurrent H3F3A mutations affecting two critical amino acids (K27 and G34) of histone H3.3 in one-third of pediatric GBM. Here, we show that each H3F3A mutation defines an epigenetic subgroup of GBM with a distinct global methylation pattern, and that they are mutually exclusive with IDH1 mutations, which characterize a third mutation-defined subgroup. Three further epigenetic subgroups were enriched for hallmark genetic events of adult GBM and/or established transcriptomic signatures. We also demonstrate that the two H3F3A mutations give rise to GBMs in separate anatomic compartments, with differential regulation of transcription factors OLIG1, OLIG2, and FOXG1, possibly reflecting different cellular origins.", 
"Epigenetic regulation of gene expression is a dynamic and reversible process that establishes normal cellular phenotypes but also contributes to human diseases. At the molecular level, epigenetic regulation involves hierarchical covalent modification of DNA and the proteins that package DNA, such as histones. Here, we review the key protein families that mediate epigenetic signalling through the acetylation and methylation of histones, including histone deacetylases, protein methyltransferases, lysine demethylases, bromodomain-containing proteins and proteins that bind to methylated histones. These protein families are emerging as druggable classes of enzymes and druggable classes of protein-protein interaction domains. In this article, we discuss the known links with disease, basic molecular mechanisms of action and recent progress in the pharmacological modulation of each class of proteins.", 
"Cancers have the ability to develop resistance to traditional therapies, and the increasing prevalence of these drug resistant cancers necessitates further research and treatment development. This paper outlines the current knowledge of mechanisms that promote or enable drug resistance, such as drug inactivation, drug target alteration, drug efflux, DNA damage repair, cell death inhibition, and the epithelial-mesenchymal transition, as well as how inherent tumor cell heterogeneity plays a role in drug resistance. It also describes the epigenetic modifications that can induce drug resistance and considers how such epigenetic factors may contribute to the development of cancer progenitor cells, which are not killed by conventional cancer therapies. Lastly, this review concludes with a discussion on the best treatment options for existing drug resistant cancers, ways to prevent the formation of drug resistant cancers and cancer progenitor cells, and future directions of study.", 
"Cancer is associated with mutated genes, and analysis of tumour-linked genetic alterations is increasingly used for diagnostic, prognostic and treatment purposes. The genetic profile of solid tumours is currently obtained from surgical or biopsy specimens; however, the latter procedure cannot always be performed routinely owing to its invasive nature. Information acquired from a single biopsy provides a spatially and temporally limited snap-shot of a tumour and might fail to reflect its heterogeneity. Tumour cells release circulating free DNA (cfDNA) into the blood, but the majority of circulating DNA is often not of cancerous origin, and detection of cancer-associated alleles in the blood has long been impossible to achieve. Technological advances have overcome these restrictions, making it possible to identify both genetic and epigenetic aberrations. A liquid biopsy, or blood sample, can provide the genetic landscape of all cancerous lesions (primary and metastases) as well as offering the opportunity to systematically track genomic evolution. This Review will explore how tumour-associated mutations detectable in the blood can be used in the clinic after diagnosis, including the assessment of prognosis, early detection of disease recurrence, and as surrogates for traditional biopsies with the purpose of predicting response to treatments and the development of acquired resistance.", 
"All mammalian cells express 3 closely related Ras proteins, termed H-Ras, K-Ras, and N-Ras, that promote oncogenesis when they are mutationally activated at codon 12, 13, or 61. Although there is a high degree of similarity among the isoforms, K-Ras mutations are far more frequently observed in cancer, and each isoform displays preferential coupling to particular cancer types. We examined the mutational spectra of Ras isoforms curated from large-scale tumor profiling and found that each isoform exhibits surprisingly distinctive codon mutation and amino-acid substitution biases. These findings were unexpected given that these mutations occur in regions that share 100% amino-acid sequence identity among the 3 isoforms. Of importance, many of these mutational biases were not due to differences in exposure to mutagens, because the patterns were still evident when compared within specific cancer types. We discuss potential genetic and epigenetic mechanisms, as well as isoform-specific differences in protein structure and signaling, that may promote these distinct mutation patterns and differential coupling to specific cancers. Cancer Res; 72(10); 2457-67. (C) 2012 AACR.", 
"Epigenetic aberrations, which are recognized as key drivers of several human diseases, are often caused by genetic defects that result in functional deregulation of epigenetic proteins, their altered expression and/or their atypical recruitment to certain gene promoters. Importantly, epigenetic changes are reversible, and epigenetic enzymes and regulatory proteins can be targeted using small molecules. This Review discusses the role of altered expression and/or function of one class of epigenetic regulators histone deacetylases (HDACs) - and their role in cancer, neurological diseases and immune disorders. We highlight the development of small-molecule HDAC inhibitors and their use in the laboratory, in preclinical models and in the clinic.", 
"In the mammalian genome, DNA methylation is an epigenetic mechanism involving the transfer of a methyl group onto the C5 position of the cytosine to form 5-methylcytosine. DNA methylation regulates gene expression by recruiting proteins involved in gene repression or by inhibiting the binding of transcription factor(s) to DNA. During development, the pattern of DNA methylation in the genome changes as a result of a dynamic process involving both de novo DNA methylation and demethylation. As a consequence, differentiated cells develop a stable and unique DNA methylation pattern that regulates tissue-specific gene transcription. In this chapter, we will review the process of DNA methylation and demethylation in the nervous system. We will describe the DNA (de) methylation machinery and its association with other epigenetic mechanisms such as histone modifications and noncoding RNAs. Intriguingly, postmitotic neurons still express DNA methyltransferases and components involved in DNA demethylation. Moreover, neuronal activity can modulate their pattern of DNA methylation in response to physiological and environmental stimuli. The precise regulation of DNA methylation is essential for normal cognitive function. Indeed, when DNA methylation is altered as a result of developmental mutations or environmental risk factors, such as drug exposure and neural injury, mental impairment is a common side effect. The investigation into DNA methylation continues to show a rich and complex picture about epigenetic gene regulation in the central nervous system and provides possible therapeutic targets for the treatment of neuropsychiatric disorders. Neuropsychopharmacology Reviews (2013) 38, 23-38; doi:10.1038/npp.2012.112; published online 11 July 2012", 
"Genetic alterations and epigenetic dysregulation in cancer cells create a vast array of neoepitooes potentially recognizable by the immune system. Immune checkpoint blockade has the capacity to enhance and sustain endogenous immunity against non-mutated tumor-associated antigens as well as uniquely mutant antigens, establishing durable tumor control. Recent evidence from preclinical models highlights the pivotal role of the Programmed Death-1 (PD-1) T cell co-receptor and its ligands, B7-H1/PD-L1 and B7-DC/PD-L2, in maintaining an immunosuppressive tumor microenvironment. Encouraging early clinical results using blocking agents against components of the PD-1 pathway have validated its importance as a target for cancer immunotherapy.", 
"Epigenetic enzymes are often dysregulated in human tumors through mutation, altered expression, or inappropriate recruitment to certain loci. The identification of these enzymes and their partner proteins has driven the rapid development of small-molecule inhibitors that target the cancer epigenome. Herein, we discuss the influence of aberrantly regulated histone deacetylases (HDACs) in tumorigenesis. We examine HDAC inhibitors (HDACis) targeting class I, II, and IV HDACs that are currently under development for use as anticancer agents following the FDA approval of two HDACis, vorinostat and romidepsin.", 
"Epigenetics is one of the most promising and expanding fields in the current biomedical research landscape. Since the inception of epigenetics in the 1940s, the discoveries regarding its implications in normal and disease biology have not stopped, compiling a vast amount of knowledge in the past decade. The field has moved from just one recognized marker, DNA methylation, to a variety of others, including a wide spectrum of histone modifications. From the methodological standpoint, the successful initial single gene candidate approaches have been complemented by the current comprehensive epigenomic approaches that allow the interrogation of genomes to search for translational applications in an unbiased manner. Most important, the discovery of mutations in the epigenetic machinery and the approval of the first epigenetic drugs for the treatment of subtypes of leukemias and lymphomas has been an eye-opener for many biomedical scientists and clinicians. Herein, we will summarize the progress in the field of cancer epigenetics research that has reached mainstream oncology in the development of new biomarkers of the disease and new pharmacological strategies.", 
"With rare exceptions, spontaneous tumors originate from a single cell. Yet, at the time of clinical diagnosis, the majority of human tumors display startling heterogeneity in many morphological and physiological features, such as expression of cell surface receptors, proliferative and angiogenic potential. To a substantial extent, this heterogeneity might be attributed to morphological and epigenetic plasticity, but there is also strong evidence for the co-existence of genetically divergent tumor cell clones within tumors. In this perspective, we summarize the sources of intra-tumor phenotypic heterogeneity with emphasis on genetic heterogeneity. We review experimental evidence for the existence of both intra-tumor clonal heterogeneity as well as frequent evolutionary divergence between primary tumors and metastatic outgrowths. Furthermore, we discuss potential biological and clinical implications of intra-tumor clonal heterogeneity. (C) 2009 Elsevier B.V. All rights reserved.", 
"Thyroid cancer is a common endocrine malignancy. There has been exciting progress in understanding its molecular pathogenesis in recent years, as best exemplified by the elucidation of the fundamental role of several major signalling pathways and related molecular derangements. Central to these mechanisms are the genetic and epigenetic alterations in these pathways, such as mutation, gene copy-number gain and aberrant gene methylation. Many of these molecular alterations represent novel diagnostic and prognostic molecular markers and therapeutic targets for thyroid cancer, which provide unprecedented opportunities for further research and clinical development of novel treatment strategies for this cancer.", 
"During the course of malignant cancer progression, neoplastic cells undergo dynamic and reversible transitions between multiple phenotypic states, the extremes of which are defined by the expression of epithelial and mesenchymal phenotypes. This plasticity is enabled by underlying shifts in epigenetic regulation. A small cohort of pleiotropically acting transcription factors is widely recognized to effect these shifts by controlling the expression of a constituency of key target genes. These master regulators depend on complex epigenetic regulatory mechanisms, notably the induction of changes in the modifications of chromatin-associated histones, in order to achieve the widespread changes in gene expression observed during epithelial-mesenchymal transitions (EMTs). These associations indicate that an understanding of the functional interactions between such EMT-inducing transcription factors and the modulators of chromatin configuration will provide crucial insights into the fundamental mechanisms underlying cancer progression and may, in the longer term, generate new diagnostic and therapeutic modalities for treating high-grade malignancies.", 
"One-carbon metabolism involving the folate and methionine cycles integrates nutritional status from amino acids, glucose and vitamins, and generates diverse outputs, such as the biosynthesis of lipids, nucleotides and proteins, the maintenance of redox status and the substrates for methylation reactions. Long considered a 'housekeeping' process, this pathway has recently been shown to have additional complexity. Genetic and functional evidence suggests that hyperactivation of this pathway is a driver of oncogenesis and establishes a link to cellular epigenetic status. Given the wealth of clinically available agents that target one-carbon metabolism, these new findings could present opportunities for translation into precision cancer medicine.", 
"Lysine acetylation is a key mechanism that regulates chromatin structure; aberrant acetylation levels have been linked to the development of several diseases. Acetyl-lysine modifications create docking sites for bromodonnains, which are small interaction modules found on diverse proteins, some of which have a key role in the acetylation-dependent assembly of transcriptional regulator complexes. These complexes can then initiate transcriptional programmes that result in phenotypic changes. The recent discovery of potent and highly specific inhibitors for the BET (bromodonnain and extra-terminal) family of bromodomains has stimulated intensive research activity in diverse therapeutic areas, particularly in oncology, where BET proteins regulate the expression of key oncogenes and anti-apoptotic proteins. In addition, targeting BET bromodonnains could hold potential for the treatment of inflammation and viral infection. Here, we highlight recent progress in the development of bromodomain inhibitors, and their potential applications in drug discovery.", 
"Post-translational modification of histones provides an important regulatory platform for processes such as gene transcription and DNA damage repair. It has become increasingly apparent that the misregulation of histone modification, which is caused by the deregulation of factors that mediate the modification installation, removal and/or interpretation, actively contributes to human cancer. In this Review, we summarize recent advances in understanding the interpretation of certain histone methylations by plant homeodomain finger-containing proteins, and how misreading, miswriting and mis-erasing of histone methylation marks can be associated with oncogenesis and progression. These observations provide us with a greater mechanistic understanding of epigenetic alterations in human cancers and might also help direct new therapeutic interventions in the future.", 
"DNA methylation is one of the most intensely studied epigenetic modifications in mammals. In normal cells, it assures the proper regulation of gene expression and stable gene silencing. DNA methylation is associated with histone modifications and the interplay of these epigenetic modifications is crucial to regulate the functioning of the genome by changing chromatin architecture. The covalent addition of a methyl group occurs generally in cytosine within CpG dinucleotides which are concentrated in large clusters called CpG islands. DNA methyltransferases are responsible for establishing and maintenance of methylation pattern. It is commonly known that inactivation of certain tumor-suppressor genes occurs as a consequence of hypermethylation within the promoter regions and a numerous studies have demonstrated a broad range of genes silenced by DNA methylation in different cancer types. On the other hand, global hypomethylation, inducing genomic instability, also contributes to cell transformation. Apart from DNA methylation alterations in promoter regions and repetitive DNA sequences, this phenomenon is associated also with regulation of expression of noncoding RNAs such as microRNAs that may play role in tumor suppression. DNA methylation seems to be promising in putative translational use in patients and hypermethylated promoters may serve as biomarkers. Moreover, unlike genetic alterations, DNA methylation is reversible what makes it extremely interesting for therapy approaches. The importance of DNA methylation alterations in tumorigenesis encourages us to decode the human epigenome. Different DNA methylome mapping techniques are indispensable to realize this project in the future. (C) 2010, Elsevier Inc.", 
"Epigenetic and genetic alterations have long been thought of as two separate mechanisms participating in carcinogenesis. A recent outcome of whole exome sequencing of thousands of human cancers has been the unexpected discovery of many inactivating mutations in genes that control the epigenome. These mutations have the potential to disrupt DNA methylation patterns, histone modifications, and nucleosome positioning and hence, gene expression. Genetic alteration of the epigenome therefore contributes to cancer just as epigenetic process can cause point mutations and disable DNA repair functions. This crosstalk between the genome and the epigenome offers new possibilities for therapy.", 
"The epithelial-mesenchymal transition (EMT) confers mesenchymal properties on epithelial cells and has been closely associated with the acquisition of aggressive traits by carcinoma cells. EMT programs are orchestrated by a set of pleiotropically acting transcription factors (TFs). The actions of these EMT-TFs enable the early steps of metastasis: local invasion and subsequent dissemination of carcinoma cells to distant sites. However, in most malignancies, the subsequent outgrowth of micrometastatic deposits into macroscopic metastases has the greatest impact on clinical progression. Such metastatic colonization reflects the ability of disseminated tumor cells to adapt to a foreign tissue microenvironment. The outgrowth of a metastasis is also thought to be associated with self-renewal, the defining cellular trait of cancer stem cells (CSCs), also termed tumor-initiating cells. Importantly, molecular links between EMT-TFs and self-renewal have emerged, suggesting that EMT programs play critical roles both early and late in the metastatic cascade. The genetic and epigenetic mechanisms that regulate the activation of EMT-TFs and the traits they induce are areas under intensive investigation. Such studies may provide new opportunities for therapeutic intervention and help to overcome tumor heterogeneity and therapeutic resistance. (C) 2012 Elsevier Ltd. All rights reserved.", 
"The transcription factor Nrf2 (NF-E2-related factor 2) plays a vital role in maintaining cellular homeostasis, especially upon the exposure of cells to chemical or oxidative stress, through its ability to regulate the basal and inducible expression of a multitude of antioxidant proteins, detoxification enzymes and xenobiotic transporters. In addition, Nrf2 contributes to diverse cellular functions including differentiation, proliferation, inflammation and lipid synthesis and there is an increasing association of aberrant expression and/or function of Nrf2 with pathologies including cancer, neurodegeneration and cardiovascular disease. The activity of Nrf2 is primarily regulated via its interaction with Keap1 (Kelch-like ECH-associated protein 1), which directs the transcription factor for proteasomal degradation. Although it is generally accepted that modification (e.g. chemical adduction, oxidation, nitrosylation or glutathionylation) of one or more critical cysteine residues in Keap1 represents a likely chemico-biological trigger for the activation of Nrf2, unequivocal evidence for such a phenomenon remains elusive. An increasing body of literature has revealed alternative mechanisms of Nrf2 regulation, including phosphorylation of Nrf2 by various protein kinases (PKC, PI3K/Akt, GSK-3 beta, JNK), interaction with other protein partners (p21, caveolin-1) and epigenetic factors (micro-RNAs -144, -28 and -200a, and promoter methylation). These and other processes are potentially important determinants of Nrf2 activity, and therefore may contribute to the maintenance of cellular homeostasis. Here, we dissect evidence supporting these Keap1-dependent and -independent mechanisms of Nrf2 regulation. Furthermore, we highlight key knowledge gaps in this important field of biology, and suggest how these may be addressed experimentally. (C) 2012 Elsevier Inc. All rights reserved.", 
"It is now generally accepted that vitamin D deficiency is a worldwide health problem that affects not only musculoskeletal health but also a wide range of acute and chronic diseases. However, there remains cynicism about the lack of randomized controlled trials to support the association studies regarding the nonskeletal health benefits of vitamin D. This review was obtained by searching English-language studies published up to April 1, 2013, in PubMed, MEDLINE, and the Cochrane Central Register of Controlled Trials (search terms: vitamin D and supplementation) and focuses on recent challenges regarding the definition of vitamin D deficiency and how to achieve optimal serum 25-hydroxyvitamin D concentrations from dietary sources, supplements, and sun exposure. The effect of vitamin D on fetal programming epigenetics and gene regulation could potentially explain why vitamin D has been reported to have such wide-ranging health benefits throughout life. There is potentially a great upside to increasing the vitamin D status of children and adults worldwide for improving musculoskeletal health and reducing the risk of chronic illnesses, including some cancers, autoimmune diseases, infectious diseases, type 2 diabetes mellitus, neurocognitive disorders, and mortality. (c) 2013 Mayo Foundation for Medical Education and Research", 
"Hematopoietic cells, including lymphoid and myeloid cells, can develop into phenotypically distinct 'subpopulations' with different functions. However, evidence indicates that some of these subpopulations can manifest substantial plasticity (that is, undergo changes in their phenotype and function). Here we focus on the occurrence of phenotypically distinct subpopulations in three lineages of myeloid cells with important roles in innate and acquired immunity: macrophages, mast cells and neutrophils. Cytokine signals, epigenetic modifications and other microenvironmental factors can substantially and, in some cases, rapidly and reversibly alter the phenotype of these cells and influence their function. This suggests that regulation of the phenotype and function of differentiated hematopoietic cells by microenvironmental factors, including those generated during immune responses, represents a common mechanism for modulating innate or adaptive immunity.", 
"Cancer is a disease of aberrant gene expression. While the genetic causes of cancer have been intensively studied, it is becoming evident that a large proportion of cancer susceptibility cannot be attributed to variation in protein-coding sequences. This is highlighted by genome-wide association studies in cancer that reveal that more than 80% of cancer-associated SNPs occur in noncoding regions of the genome. In this review, we posit that a significant fraction of the genetic aetiology of cancer is exacted by noncoding regulatory sequences, particularly by long noncoding RNAs (lncRNAs). Recent studies indicate that several cancer risk loci are transcribed into lncRNAs and these transcripts play key roles in tumorigenesis. We discuss the epigenetic and other mechanisms through which lncRNAs function and how they contribute to each stage of cancer progression, understanding of which will be crucial for realising new opportunities in cancer diagnosis and treatment. Long noncoding RNAs play important roles in almost every aspect of cell biology from nuclear organisation and epigenetic regulation to post-transcriptional regulation and splicing, and we link these processes to the hallmarks and genetics of cancer. Finally, we highlight recent progress and future potential in the application of lncRNAs as therapeutic targets and diagnostic markers.", 
"We hypothesized that DNA methylation distributes into specific patterns in cancer cells, which reflect critical biological differences. We therefore examined the methylation profiles of 344 patients with acute myeloid leukemia (AML). Clustering of these patients by methylation data segregated patients into 16 groups. Five of these groups defined new AML subtypes that shared no other known feature. In addition, DNA methylation profiles segregated patients with CEBPA aberrations from other subtypes of leukemia, defined four epigenetically distinct forms of AML with NPM1 mutations, and showed that established AML1-ETO, CBFb-MYH11, and PML-RARA leukemia entities are associated with specific methylation profiles. We report a 15 gene methylation classifier predictive of overall survival in an independent patient cohort (p < 0.001, adjusted for known covariates).", 
"The histone 3 lysine 79 (H3K79) methyltransferase Dot1l has been implicated in the development of leukemias bearing translocations of the Mixed Lineage Leukemia (MLL) gene. We identified the MLL-fusion targets in an MLL-AF9 leukemia model, and conducted epigenetic profiling for H3K79me2, H3K4me3, H3K27me3, and H3K36me3 in hematopoietic progenitor and leukemia stem cells (LSCs). We found abnormal profiles only for H3K79me2 on MLL-AF9 fusion target loci in LSCs. Inactivation of Dot1l led to downregulation of direct MLL-AF9 targets and an MLL translocation-associated gene expression signature, whereas global gene expression remained largely unaffected. Suppression of MLL translocation-associated gene expression corresponded with dependence of MLL-AF9 leukemia on Dot1l in vivo. These data point to DOT1L as a potential therapeutic target in MLL-rearranged leukemia.", 
"The unique abilities of human pluripotent stem cells to self-renew and to differentiate into cells of the three germ layers make them an invaluable tool for the future of regenerative medicine. However, the same properties also make them tumorigenic, and therefore hinder their clinical application. Hence, the tumorigenicity of human embryonic stem cells (HESCs) has been extensively studied. Until recently, it was assumed that human induced pluripotent stem cells (HiPSCs) would behave like their embryonic counterparts in respect to their tumorigenicity. However, a rapidly accumulating body of evidence suggests that there are important genetic and epigenetic differences between these two cell types, which seem to influence their tumorigenicity.", 
"Type 2 diabetes is now a pandemic and shows no signs of abatement. In this Seminar we review the pathophysiology of this disorder, with particular attention to epidemiology, genetics, epigenetics, and molecular cell biology. Evidence is emerging that a substantial part of diabetes susceptibility is acquired early in life, probably owing to fetal or neonatal programming via epigenetic phenomena. Maternal and early childhood health might, therefore, be crucial to the development of effective prevention strategies. Diabetes develops because of inadequate islet beta-cell and adipose-tissue responses to chronic fuel excess, which results in so-called nutrient spillover, insulin resistance, and metabolic stress. The latter damages multiple organs. Insulin resistance, while forcing beta cells to work harder, might also have an important defensive role against nutrient-related toxic effects in tissues such as the heart. Reversal of ovemutrition, healing of the beta cells, and lessening of adipose tissue defects should be treatment priorities.", 
"Since the discovery of vitamin C, the number of its known biological functions is continually expanding. Both the names ascorbic acid and vitamin C reflect its antiscorbutic properties due to its role in the synthesis of collagen in connective tissues. Ascorbate acts as an electron-donor keeping iron in the ferrous state thereby maintaining the full activity of collagen hydroxylases; parallel reactions with a variety of dioxygenases affect the expression of a wide array of genes, for example via the HIF system, as well as via the epigenetic landscape of cells and tissues. In fact, all known physiological and biochemical functions of ascorbate are due to its action as an electron donor. The ability to donate one or two electrons makes AscH(-) an excellent reducing agent and antioxidant. Ascorbate readily undergoes pH-dependent autoxidation producing hydrogen peroxide (H2O2). In the presence of catalytic metals this oxidation is accelerated. In this review, we show that the chemical and biochemical nature of ascorbate contribute to its antioxidant as well as its prooxidant properties. Recent pharmacokinetic data indicate that intravenous (i.v.) administration of ascorbate bypasses the tight control of the gut producing highly elevated plasma levels; ascorbate at very high levels can act as prodrug to deliver a significant flux of H2O2 to tumors. This new knowledge has rekindled interest and spurred new research into the clinical potential of pharmacological ascorbate. Knowledge and understanding of the mechanisms of action of pharmacological ascorbate bring a rationale to its use to treat disease especially the use of i.v. delivery of pharmacological ascorbate as an adjuvant in the treatment of cancer. Published by Elsevier B.V.", 
"Along with the wide use of pesticides in the world, the concerns over their health impacts are rapidly growing. There is a huge body of evidence on the relation between exposure to pesticides and elevated rate of chronic diseases such as different types of cancers, diabetes, neurodegenerative disorders like Parkinson, Alzheimer, and amyotrophic lateral sclerosis (ALS), birth defects, and reproductive disorders. There is also circumstantial evidence on the association of exposure to pesticides with some other chronic diseases like respiratory problems, particularly asthma and chronic obstructive pulmonary disease (COPD), cardiovascular disease such as atherosclerosis and coronary artery disease, chronic nephropathies, autoimmune diseases like systemic lupus erythematous and rheumatoid arthritis, chronic fatigue syndrome, and aging. The common feature of chronic disorders is a disturbance in cellular homeostasis, which can be induced via pesticides' primary action like perturbation of ion channels, enzymes, receptors, etc., or can as well be mediated via pathways other than the main mechanism. In this review, we present the highlighted evidence on the association of pesticide's exposure with the incidence of chronic diseases and introduce genetic damages, epigenetic modifications, endocrine disruption, mitochondrial dysfunction, oxidative stress, endoplasmic reticulum stress and unfolded protein response (UPR), impairment of ubiquitin proteasome system, and defective autophagy as the effective mechanisms of action. (C) 2013 Elsevier Inc. All rights reserved.", 
"Phosphorylation of the Ser-139 residue of the histone variant H2AX, forming gamma H2AX, is an early cellular response to the induction of DNA double-strand breaks. Detection of this phosphorylation event has emerged as a highly specific and sensitive molecular marker for monitoring DNA damage initiation and resolution. Further, analysis of gamma H2AX foci has numerous other applications including, but not limited to, cancer and aging research. Quantitation of gamma H2AX foci has also been applied as a useful tool for the evaluation of the efficacy of various developmental drugs, particularly, radiation modifying compounds. This review focuses on the current status of gamma H2AX as a marker of DNA damage and repair in the context of ionizing radiation. Although the emphasis is on gamma-radiation-induced gH2AX foci, the effects of other genotoxic insults including exposure to ultraviolet rays, oxidative stress and chemical agents are also discussed. Leukemia (2010) 24, 679-686; doi: 10.1038/leu.2010.6; published online 4 February 2010", 
"Chromosomal rearrangements fusing the androgen-regulated gene TMPRSS2 to the oncogenic ETS transcription factor ERG occur in approximately 50% of prostate cancers, but how the fusion products regulate prostate cancer remains unclear. Using chromatin immunoprecipitation coupled with massively parallel sequencing, we found that ERG disrupts androgen receptor (AR) signaling by inhibiting AR expression, binding to and inhibiting AR activity at gene-specific loci, and inducing repressive epigenetic programs via direct activation of the H3K27 methyltransferase EZH2, a Polycomb group protein. These findings provide a working model in which TMPRSS2-ERG plays a critical role in cancer progression by disrupting lineage-specific differentiation of the prostate and potentiating the EZH2-mediated dedifferentiation program.", 
"Purpose of review TGF-beta acts as a potent driver of cancer progression through the induction of epithelial-mesenchymal transition (EMT), in which epithelial cells acquire mesenchymal phenotype, leading to enhanced motility and invasion. Recent reports highlight the fundamental roles of TGF-beta-induced EMT in multiple aspects of cancer progression. In this review, we focus on the novel insights into the roles of TGF-beta-induced EMT in cancer progression and the underlying mechanisms that enable TGF-beta to activate this epithelial plasticity response at transcription, translation, and posttranslational levels. Recent findings Smad-mediated transcription regulation is known to activate TGF-beta-induced EMT. More recently, novel mechanisms of epigenetic control, alternative splicing, miRNAs, translation control, and posttranslational modifications have been shown to play key roles in the control of EMT. In addition to initiating carcinoma cell invasion, TGF-beta-induced EMT can guide cancer cells to de-differentiate and gain cancer stem-cell-like properties. EMT also allows the generation of stromal cells that support and instruct cancer progression. Summary The differentiation plasticity of epithelial cells that mediates TGF-beta-induced EMT and reversion from mesenchymal to epithelial phenotype are increasingly seen as integral aspects of cancer progression that contribute to survival and dissemination of cancer cells. Further mechanistic insights under physiological conditions may lead to new therapeutic or prognostic strategies in cancer treatment.", 
"Metastases arise from residual disseminated tumour cells (DTCs). This can happen years after primary tumour treatment because residual tumour cells can enter dormancy and evade therapies. As the biology of minimal residual disease seems to diverge from that of proliferative lesions, understanding the underpinnings of this new cancer biology is key to prevent metastasis. Analysis of approximately 7 years of literature reveals a growing focus on tumour and normal stem cell quiescence, extracellular and stromal microenvironments, autophagy and epigenetics as mechanisms that dictate tumour cell dormancy. In this Review, we attempt to integrate this information and highlight both the weaknesses and the strengths in the field to provide a framework to understand and target this crucial step in cancer progression.", 
"Colorectal cancer (CRC) is a heterogeneous disease, including at least three major forms: hereditary, sporadic and colitis-associated CRC. A large body of evidence indicates that genetic mutations, epigenetic changes, chronic inflammation, diet and lifestyle are the risk factors for CRC. As elevated cyclooxygenase-2 (COX-2) expression was found in most CRC tissue and is associated with worse survival among CRC patients, investigators have sought to evaluate the effects of nonsteroidal anti-inflammatory drugs (NSAIDs) and selective COX-2 inhibitors (COXIBs) on CRC. The epidemiological studies, clinical trials and animal experiments indicate that NSAIDs are among the most promising chemopreventive agents for this disease. NSAIDs exert their antiinflammatory and antitumor effects primarily by reducing prostaglandin production by inhibition of COX-2 activity. In this review, we highlight breakthroughs in our understanding of the roles of COX-2 in CRC and inflammatory bowel disease. These recent data provide a rationale for re-evaluating COX-2 as both the prognostic and the predictive marker in a wide variety of malignancies and for renewing the interest in evaluating relative benefits and risk of COXIBs in appropriately selected patients for cancer prevention and treatment. Oncogene (2010) 29, 781-788; doi:10.1038/onc.2009.421; published online 30 November 2009", 
"Glioblastoma is the most frequent and malignant brain tumor. The vast majority of glioblastomas (similar to 90%) develop rapidly de novo in elderly patients, without clinical or histologic evidence of a less malignant precursor lesion (primary glioblastomas). Secondary glioblastomas progress from low-grade diffuse astrocytoma or anaplastic astrocytoma. They manifest in younger patients, have a lesser degree of necrosis, are preferentially located in the frontal lobe, and carry a significantly better prognosis. Histologically, primary and secondary glioblastomas are largely indistinguishable, but they differ in their genetic and epigenetic profiles. Decisive genetic signposts of secondary glioblastoma are IDH1 mutations, which are absent in primary glioblastomas and which are associated with a hypermethylation phenotype. IDH1 mutations are the earliest detectable genetic alteration in precursor low-grade diffuse astrocytomas and in oligodendrogliomas, indicating that these tumors are derived from neural precursor cells that differ from those of primary glioblastomas. In this review, we summarize epidemiologic, clinical, histopathologic, genetic, and expression features of primary and secondary glioblastomas and the biologic consequences of IDH1 mutations. We conclude that this genetic alteration is a definitive diagnostic molecular marker of secondary glioblastomas and more reliable and objective than clinical criteria. Despite a similar histologic appearance, primary and secondary glioblastomas are distinct tumor entities that originate from different precursor cells and may require different therapeutic approaches. Clin Cancer Res; 19(4); 764-72. (c) 2012 AACR.", 
"Myriad genetic and epigenetic alterations are required to drive normal cells toward malignant transformation. These somatic events commandeer many signaling pathways that cooperate to endow aspiring cancer cells with a full range of biological capabilities needed to grow, disseminate and ultimately kill its host. Cancer genomes are highly rearranged and are characterized by complex translocations and regional copy number alterations that target loci harboring cancer-relevant genes. Efforts to uncover the underlying mechanisms driving genome instability in cancer have revealed a prominent role for telomeres. Telomeres are nucleoprotein structures that protect the ends of eukaryotic chromosomes and are particularly vulnerable due to progressive shortening during each round of DNA replication and, thus, a lifetime of tissue renewal places the organism at risk for increasing chromosomal instability. Indeed, telomere erosion has been documented in aging tissues and hyperproliferative disease states-conditions strongly associated with increased cancer risk. Telomere dysfunction can produce the opposing pathophysiological states of degenerative aging or cancer with the specific outcome dictated by the integrity of DNA damage checkpoint responses. In most advanced cancers, telomerase is reactivated and serves to maintain telomere length and emerging data have also documented the capacity of telomerase to directly regulate cancer-promoting pathways. This review covers the role of telomeres and telomerase in the biology of normal tissue stem/progenitor cells and in the development of cancer.", 
"Conventional chemotherapeutics and targeted antineoplastic agents have been developed based on the simplistic notion that cancer constitutes a cell-autonomous genetic or epigenetic disease. However, it is becoming clear that many of the available anticancer drugs that have collectively saved millions of life-years mediate therapeutic effects by eliciting de novo or reactivating pre-existing tumor-specific immune responses. Here, we discuss the capacity of both conventional and targeted anticancer therapies to enhance the immunogenic properties of malignant cells and to stimulate immune effector cells, either directly or by subverting the immunosuppressive circuitries that preclude antitumor immune responses in cancer patients. Accumulating evidence indicates that the therapeutic efficacy of several antineoplastic agents relies on their capacity to influence the tumor-host interaction, tipping the balance toward the activation of an immune response specific for malignant cells. We surmise that the development of successful anticancer therapies will be improved and accelerated by the immunological characterization of candidate agents.", 
"Alkylating agents constitute a major class of frontline chemotherapeutic drugs that inflict cytotoxic DNA damage as their main mode of action, in addition to collateral mutagenic damage. Numerous cellular pathways, including direct DNA damage reversal, base excision repair (BER) and mismatch repair (MMR), respond to alkylation damage to defend against alkylation-induced cell death or mutation. However, maintaining a proper balance of activity both within and between these pathways is crucial for a favourable response of an organism to alkylating agents. Furthermore, the response of an individual to alkylating agents can vary considerably from tissue to tissue and from person to person, pointing to genetic and epigenetic mechanisms that modulate alkylating agent toxicity.", 
"MicroRNA (miRNA) alterations are involved in the initiation and progression of human cancer. The causes of the widespread differential expression of miRNA genes in malignant compared with normal cells can be explained by the location of these genes in cancer-associated genomic regions, by epigenetic mechanisms and by alterations in the miRNA processing machinery. MiRNA-expression profiling of human tumours has identified signatures associated with diagnosis, staging, progression, prognosis and response to treatment. In addition, profiling has been exploited to identify miRNA genes that might represent downstream targets of activated oncogenic pathways, or that target protein-coding genes involved in cancer.", 
"BACKGROUND: Epigenetic silencing of the MGMT (O(sup 6)-methylguanine-DNA methyltransferase) DNA-repair gene by promoter methylation compromises DNA repair and has been associated with longer survival in patients with glioblastoma who receive alkylating agents. METHODS: We tested the relationship between MGMT silencing in the tumor and the survival of patients who were enrolled in a randomized trial comparing radiotherapy alone with radiotherapy combined with concomitant and adjuvant treatment with temozolomide. The methylation status of the MGMT promoter was determined by methylation-specific polymerase-chain-reaction analysis. RESULTS: The MGMT promoter was methylated in 45 percent of 206 assessable cases. Irrespective of treatment, MGMT promoter methylation was an independent favorable prognostic factor (P<0.001 by the log-rank test; hazard ratio, 0.45; 95 percent confidence interval, 0.32 to 0.61). Among patients whose tumor contained a methylated MGMT promoter, a survival benefit was observed in patients treated with temozolomide and radiotherapy; their median survival was 21.7 months (95 percent confidence interval, 17.4 to 30.4), as compared with 15.3 months (95 percent confidence interval, 13.0 to 20.9) among those who were assigned to only radiotherapy (P=0.007 by the log-rank test). In the absence of methylation of the MGMT promoter, there was a smaller and statistically insignificant difference in survival between the treatment groups. CONCLUSIONS: Patients with glioblastoma containing a methylated MGMT promoter benefited from temozolomide, whereas those who did not have a methylated MGMT promoter did not have such a benefit.", 
" ", 
"Transitions between epithelial and mesenchymal states have crucial roles in embryonic development. Emerging data suggest a role for these processes in regulating cellular plasticity in normal adult tissues and in tumours, where they can generate multiple, distinct cellular subpopulations contributing to intratumoural heterogeneity. Some of these subpopulations may exhibit more differentiated features, whereas others have characteristics of stem cells. Owing to the importance of these tumour-associated phenotypes in metastasis and cancer-related mortality, targeting the products of such cellular plasticity is an attractive but challenging approach that is likely to lead to improved clinical management of cancer patients.", 
"Histone deacetylases (HDACs) are enzymes involved in the remodelling of chromatin, and have a key role in the epigenetic regulation of gene expression. In addition, the activity of non-histone proteins can be regulated through HDAC-mediated hypoacetylation. In recent years, inhibition of HDACs has emerged as a potential strategy to reverse aberrant epigenetic changes associated with cancer, and several classes of HDAC inhibitors have been found to have potent and specific anticancer activities in preclinical studies. However, such studies have also indicated that the effects of HDAC inhibitors could be considerably broader and more complicated than originally understood. Here we summarize recent advances in the understanding of the molecular events that underlie the anticancer effects of HDAC inhibitors, and discuss how such information could be used in optimizing the development and application of these agents in the clinic, either as monotherapies or in combination with other anticancer drugs.", 
" ", 
"Histone deacetylases ( HDACs) are considered to be among the most promising targets in drug development for cancer therapy, and first- generation histone deacetylase inhibitors ( HDACi) are currently being tested in phase I/ II clinical trials. A wide- ranging knowledge of the role of HDACs in tumorigenesis, and of the action of HDACi, has been achieved. However, several basic aspects are not yet fully understood. Investigating these aspects in the context of what we now understand about HDACi action both in vitro and in vivo will further improve the design of optimized clinical protocols.", 
"MicroRNAs (miRNAs) are small, noncoding RNAs with important functions in development, cell differentiation, and regulation Of Cell cycle and apoptosis. MiRNA expression is deregulated in cancer by a variety of mechanisms including amplification, deletion, mutation, and epigenetic silencing. Several studies have now shown that miRNAs arc involved in the initiation and progression of cancer. In this review, we briefly describe miRNA biogenesis and discuss how miRNAs can act as oncogenes and tumor Suppressors. We also address the role of miRNAs in the diagnosis, prognosis, and treatment of cancer.", 
"Resistance of human tumors to anticancer drugs is most often ascribed to gene mutations, gene amplification, or epigenetic changes that influence the uptake, metabolism, or export of drugs from single cells. Another important yet little-appreciated cause of anticancer drug resistance is the limited ability of drugs to penetrate tumor tissue and to reach all of the tumor cells in a potentially lethal concentration. To reach all viable cells in the tumor, anticancer drugs must be delivered efficiently through the tumor vasculature, cross the vessel wall, and traverse the tumor tissue. In addition, heterogeneity within the tumor microenvironment leads to marked gradients in the rate of cell proliferation and to regions of hypoxia and acidity, all of which can influence the sensitivity of the tumor cells to drug treatment. In this review, we describe how the tumor microenvironment may be involved in the resistance of solid tumors to chemotherapy and discuss potential strategies to improve the effectiveness of drug treatment by modifying factors relating to the tumor microenvironment.", 
"Chromatin alterations have been associated with all stages of tumour formation and progression. The best characterized are epigenetically mediated transcriptional-silencing events that are associated with increases in DNA methylation - particularly at promoter regions of genes that regulate important cell functions. Recent evidence indicates that epigenetic changes might 'addict' cancer cells to altered signal-transduction pathways during the early stages of tumour development. Dependence on these pathways for cell proliferation or survival allows them to acquire genetic mutations in the same pathways, providing the cell with selective advantages that promote tumour progression. Strategies to reverse epigenetic gene silencing might therefore be useful in cancer prevention and therapy.", 
"Epithelial ovarian cancer (EOC) is the sixth most common cancer in women worldwide and, despite advances in detection and therapies, it still represents the most lethal gynecologic malignancy in the industrialized countries. Unfortunately, still relatively little is known about the molecular events that lead to the development of this highly aggressive disease. The relatively recent discovery of microRNAs (miRNA), a class of small noncoding RNAs targeting multiple mRNAs and triggering translation repression and/or RNA degradation, has revealed the existence of a new level of gene expression regulation. Multiple studies involving various types of human cancers proved that miRNAs have a causal role in tumorigenesis. Here we show that, in comparison to normal ovary, miRNAs are aberrantly expressed in human ovarian cancer. The overall miRNA expression could clearly separate normal versus cancer tissues. The most significantly overexpressed miRNAs were miR-200a, miR-141, miR-200c, and miR200b, whereas miR-199a, miR-140, miR-145, and miR-125b1 were among the most down-modulated miRNAs. We could also identify miRNAs whose expression was correlated with specific ovarian cancer biopathologic features, such as histotype, lymphovascular and organ invasion, and involvement of ovarian surface. Moreover, the levels of miR-21, miR-203, and miR-205, up-modulated in ovarian carcinomas compared with normal tissues, were significantly increased after 5-aza-2 '-deoxycytidine demethylating treatment of OVCAR3 cells, suggesting that the DNA hypomethylation could be the mechanism responsible for their overexpression. Our results indicate that miRNAs might play a role in the pathogenesis of human EOC and identify altered miRNA gene methylation as a possible epigenetic mechanism involved in their aberrant expression.", 
"Polycomb group (PcG) proteins are epigenetic gene silencers that are implicated in neoplastic development. Their oncogenic function might be associated with their well-established role in the maintenance of embryonic and adult stem cells. In this review, we discuss new insights into the possible mechanisms by which PcGs regulate cellular identity, and speculate how these functions might be relevant during tumorigenesis.", 
"Expression profiling of T24 cells revealed that 17 out of 313 human miRNAs were upregulated more than 3-fold by simultaneous treatment with the chromatin-modifying drugs 5-aza-2'-deoxycytidine and 4-phenylbutyric acid. One of these, miR-127, is embedded in a CpG island and is highly induced from its own promoter after treatment. miR-127 is usually expressed as part of a miRNA cluster in normal cells but not in cancer cells, suggesting that it is subject to epigenetic silencing. In addition, the proto-oncogene BCL6, a potential target of miR-127, was translationally downregulated after treatment. These results suggest that DNA demethylation and histone deacetylase inhibition can activate expression of miRNAs that may act as tumor suppressors.", 
"The initiation and progression of cancer is controlled by both genetic and epigenetic events. Unlike genetic alterations, which are almost impossible to reverse, epigenetic aberrations are potentially reversible, allowing the malignant cell population to revert to a more normal state. With the advent of numerous drugs that target specific enzymes involved in the epigenetic regulation of gene expression, the utilization of epigenetic targets is emerging as an effective and valuable approach to chemotherapy as well as chemoprevention of cancer.", 
"Interferon-gamma (IFN-,gamma) is crucial for immunity against intracellular pathogens and for tumor control. However, aberrant IFN-gamma expression has been associated with a number of autoinftammatory and autoimmune diseases. This cytokine is produced predominantly by natural killer (NK) and natural killer T (NKT) cells as part of the innate immune response, and by Th1 CD4 and CD8 cytotoxic T lymphocyte (CTL) effector T cells once antigen-specific immunity develops. Herein, we briefly review the functions of IFN-gamma, the cells that produce it, the cell extrinsic signals that induce its production and influence the differentiation of naive T cells into IFN-gamma-producing effector T cells, and the signaling pathways and transcription factors that facilitate, induce, or repress production of this cytokine. We then review and discuss recent insights regarding the molecular regulation of IFN-gamma, focusing on work that has led to the identification and characterization of distal regulatory elements and epigenetic modifications with the IFN-gamma locus (lfng) that govern its expression. The epigenetic modifications and three-dimensional structure of the lfng locus in naive CD4 T cells, and the modifications they undergo as these cells differentiate into effector T cells, suggest a model whereby the chromatin architecture of lfng is poised to facilitate either rapid opening or silencing during Th1 or Th2 differentiation, respectively.", 
"Multipotential naive CD4(+) T cells differentiate into distinct lineages including T helper 1 (Th1), Th2, Th17, and inducible T regulatory (iTreg) cells. The remarkable diversity of CD4(+) T cells begs the question whether the observed changes reflect terminal differentiation with heritable epigenetic modifications or plasticity in T cell responses. We generated genome-wide histone H3 lysine 4 (H3K4) and lysine 27 (H3K27) trimethylation maps in naive, Th1, Th2, Th17, iTreg, and natural Treg (nTreg) cells. We found that although modifications of signature-cytokine genes (Ifng, II4, and II17) partially conform to the expectation of lineage commitment, genes encoding transcription factors like Tbx21 exhibit a broad spectrum of epigenetic states, consistent with our demonstration of T-bet and interferon-gamma induction in nTreg cells. Our data suggest an epigenetic mechanism underlying the specificity and plasticity of effector and regulatory T cells and also provide a framework for understanding complexity of CD4(+) T helper cell differentiation.", 
"Translocations that involve the mixed lineage leukaemia (MLL) gene identify a unique group of acute leukaemias, and often predict a poor prognosis. The MLL gene encodes a DNA-binding protein that methylates histone H3 lysine 4 (H3K4), and positively regulates gene expression including multiple Hox genes. Leukaemogenic MLL translocations encode MLL fusion proteins that have lost H3K4 methyltransferase activity. A key feature of MLL fusion proteins is their ability to efficiently transform haematopoietic cells into leukaemia stem cells. The link between a chromatin modulator and leukaemia stem cells provides support for epigenetic landscapes as an important part of leukaemia and normal stem-cell development.", 
"Cyclin-dependent kinases (cdks) are critical regulators of cell cycle progression and RNA transcription. A variety of genetic and epigenetic events cause universal overactivity of the cell cycle cdks in human cancer, and their inhibition can lead to both cell cycle arrest and apoptosis. However, built-in redundancy may limit the effects of highly selective cdk inhibition. Cdk4/6 inhibition has been shown to induce potent G, arrest in vitro and tumor regression in vivo; cdk2/1 inhibition has the most potent effects during the S and G(2) phases and induces E2F transcription factor-dependent cell death. Modulation of cdk2 and cdk1 activities also affects survival checkpoint responses after exposure to DNA-damaging and microtubule-stabilizing agents. The transcriptional cdks phosphorylate the carboxy-terminal domain of RNA polymerase II, facilitating efficient transcriptional initiation and elongation. Inhibition of these cdks primarily affects the accumulation of transcripts with short half-lives, including those encoding antiapoptosis family members, cell cycle regulators, as well as p53 and nuclear factor-kappa B-responsive gene targets. These effects may account for apoptosis induced by cdk9 inhibitors, especially in malignant hematopoietic cells, and may also potentiate cytotoxicity mediated by disruption of a variety of pathways in many transformed cell types. Current work is focusing on overcoming pharmacokinetic barriers that hindered development of flavopiridol, a pan-cdk inhibitor, as well as assessing novel classes of compounds potently targeting groups of cell cycle cdks (cdk4/6 or cdk2/1) with variable effects on the transcriptional cdks 7 and 9. These efforts will establish whether the strategy of cdk inhibition is able to produce therapeutic benefit in the majority of human tumors.", 
"Mechanisms of constitutive NF-kappa B signaling in multiple myeloma are unknown. An inhibitor of I kappa B kinase beta(IKK beta) targeting the classical NF-kappa B pathway was lethal to many myeloma cell lines. Several cell lines had elevated expression of NIK due to genomic alterations or protein stabilization, while others had inactivating mutations of TRAF3; both kinds of abnormality triggered the classical and alternative NF-kappa B pathways. A majority of primary myeloma patient samples and cell lines had elevated NF-kappa B target gene expression, often associated with genetic or epigenetic alteration of NIK, TRAF3, CYLD, BIRC2/BIRC3, CD40, NFKB1, or NFKB2. These data demonstrate that addiction to the NF-kappa B pathway is frequent in myeloma and suggest that IKK beta inhibitors hold promise for the treatment of this disease.", 
"The mechanisms underlying microRNA (miRNA) disruption in human disease are poorly understood. In cancer cells, the transcriptional silencing of tumor suppressor genes by CpG island promoter hypermethylation has emerged as a common hallmark. We wondered if the same epigenetic disruption can hit miRNAs in transformed cells. To address this issue, we have used cancer cells genetically deficient for the DNA methyltransferase enzymes in combination with a miRNA expression profiling. We have observed that DNA hypomethylation induces a release of miRNA silencing in cancer cells. One of the main targets is miRNA-124a, which undergoes transcriptional inactivation by CpG island hypermethylation in human tumors from different cell types. Interestingly, we functionally link the epigenetic loss of miRNA-124a with the activation of cyclin D kinase 6, a bona fide oncogenic factor, and the phosphorylation of the retinoblastoma, a tumor suppressor gene.", 
"Cruciferous vegetables are a rich source of glucosinolates and their hydrolysis products, including indoles and isothiocyanates, and high intake of cruciferous vegetables has been associated with lower risk of lung and colorectal cancer in some epidemiological studies. Glucosinolate hydrolysis products alter the metabolism or activity of sex hormones in ways that could inhibit the development of hormone-sensitive cancers, but evidence of an inverse association between cruciferous vegetable intake and breast or prostate cancer in humans is limited and inconsistent. Organizations such as the National Cancer Institute recommend the consumption of five to nine servings of fruits and vegetables daily, but separate recommendations for cruciferous vegetables have not been established. Isothiocyanates and indoles derived from the hydrolysis of glucosinolates, such as sulforaphane and indole-3-carbinol (I3C), have been implicated in a variety of anti carcinogenic mechanisms, but deleterious effects also have been reported in some experimental protocols, including tumor promotion over prolonged periods of exposure. Epidemiological studies indicate that human exposure to isothiocyanates and indoles through cruciferous vegetable consumption may decrease cancer risk, but the protective effects may be influenced by individual genetic variation (polymorphisms) in the metabolism and elimination of isothiocyanates from the body. Cooking procedures also affect the bioavailability and intake of glucosinolates and their derivatives. Supplementation with I3C or the related dimer 3,3'-diindolylmethane (DIM) alters urinary estrogen metabolite profiles in women, but the effects of I3C and DIM on breast cancer risk are not known. Small preliminary trials in humans suggest that I3C supplementation may be beneficial in treating conditions related to human papilloma virus infection, such as cervical intraepithelial neoplasia and recurrent respiratory papillomatosis, but larger randomized controlled trials are needed. (C) 2007 Elsevier Ltd. All rights reserved.", 
"The current goal of diabetes therapy is to reduce time-averaged mean levels of glycemia, measured as HbA1c, to prevent diabetic complications. However, HbA1c only explains <25% of the variation in risk of developing complications. Because HbA1c does not correlate with glycemic variability when adjusted for mean blood glucose, we hypothesized that transient spikes of hyperglycemia may be an HbA1c-independent risk factor for diabetic complications. We show that transient hyperglycemia induces long-lasting activating epigenetic changes in the promoter of the nuclear factor kappa B (NF-kappa B) subunit p65 in aortic endothelial cells both in vitro and in nondiabetic mice, which cause increased p65 gene expression. Both the epigenetic changes and the gene expression changes persist for at least 6 d of subsequent normal glycemia, as do NF-kappa B-induced increases in monocyte chemoattractant protein 1 and vascular cell adhesion molecule 1 expression. Hyperglycemia-induced epigenetic changes and increased p65 expression are prevented by reducing mitochondrial superoxide production or superoxide-induced alpha-oxoaldehydes. These results highlight the dramatic and long-lasting effects that short-term hyperglycemic spikes can have on vascular cells and suggest that transient spikes of hyperglycemia may be an HbA1c -independent risk factor for diabetic complications.", 
"Purpose Epigenetic processes are implicated in cancer causation and progression. The acetylation status of histones regulates access of transcription factors to DNA and influences levels of gene expression. Histone deacetylase (HDAC) activity diminishes acetylation of histones, causing compaction of the DNA/histone complex. This compaction blocks gene transcription and inhibits differentiation, providing a rationale for developing HDAC inhibitors. Methods In this review, we explore the biology of the HDAC enzymes, summarize the pharmacologic properties of HDAC inhibitors, and examine results of selected clinical trials. We consider the potential of these inhibitors in combination therapy with targeted drugs and with cytotoxic chemotherapy. Results HDAC inhibitors promote growth arrest, differentiation, and apoptosis of tumor cells, with minimal effects on normal tissue. In addition to decompaction of the histone/DNA complex, HDAC inhibition also affects acetylation status and function of nonhistone proteins. HDAC inhibitors have demonstrated antitumor activity in clinical trials, and one drug of this class, vorinostat, is US Food and Drug Administration approved for the treatment of cutaneous T-cell lymphoma. Other inhibitors in advanced stages of clinical development, including depsipeptide and MGCD0103, differ from vorinostat in structure and isoenzyme specificity, and have shown activity against lymphoma, leukemia, and solid tumors. Promising preclinical activity in combination with cytotoxics, inhibitors of heat shock protein 90, and inhibitors of proteasome function have led to combination therapy trials. Conclusion HDAC inhibitors are an important emerging therapy with single-agent activity against multiple cancers, and have significant potential in combination use.", 
"Infection and chronic inflammation contribute to about 1 in 4 of all cancer cases. Mediators of the inflammatory response, e-g., cytokines, free radicals, prostaglandins and growth factors, can induce genetic and epigenetic changes including point mutations in tumor suppressor genes, DNA methylation and post-translational modifications, causing alterations in critical pathways responsible for maintaining the normal cellular homeostasis and leading to the development and progression of cancer. Recent discovery of an interaction between microRNAs and innate immunity during inflammation has further strengthened the association between inflammation and cancer. (C) 2007 Wiley-Liss, Inc.", 
"Gain-of-function mutations in NOTCH1 are common in T- cell lymphoblastic leukemias and lymphomas ( T- ALL), making this receptor a promising target for drugs such as gamma-secretase inhibitors, which block a proteolytic cleavage required for NOTCH1 activation. However, the enthusiasm for these therapies has been tempered by tumor resistance and the paucity of information on the oncogenic programs regulated by oncogenic NOTCH1. Here we show that NOTCH1 regulates the expression of PTEN ( encoding phosphatase and tensin homolog) and the activity of the phosphoinositol- 3 kinase ( PI3K)-AKT signaling pathway in normal and leukemic T cells. Notch signaling and the PI3K-AKT pathway synergize in vivo in a Drosophila melanogaster model of Notch- induced tumorigenesis, and mutational loss of PTEN is associated with human T- ALL resistance to pharmacological inhibition of NOTCH1. Overall, these findings identify transcriptional control of PTEN and regulation of the PI3K-AKT pathway as key elements of the leukemogenic program activated by NOTCH1 and provide the basis for the design of new therapeutic strategies for T- ALL.", 
"Cancer cells contain multiple genetic and epigenetic abnormalities. Despite this complexity, their growth and survival can often be impaired by the inactivation of a single oncogene. This phenomenon, called oncogene addiction, provides a rationale for molecular targeted therapy. The efficacy of this strategy requires novel methods, including integrative genomics and systems biology, to identify the state of oncogene addiction (i.e., the Achilles heel) in specific cancers. Combination therapy may also be required to prevent the escape of cancers from a given state of oncogene addiction.", 
"NFATc1 and NFATc2 are functionally redundant in the immune system, but it was suggested that NFATc1 is required exclusively for differentiation of osteoclasts in the skeletal system. Here we provide genetic evidence that NFATc1 is essential for osteoclast differentiation in vivo by adoptive transfer of NFATc1(-/-) hematopoietic stem cells to osteoclast-deficient Fos(-/-) mice, and by Fos(-/-) blastocyst complementation, thus avoiding the embryonic lethality of NFATc1(-/-) mice. However, in vitro osteoclastogenesis in NFATc1-deficient cells was rescued by ectopic expression of NFATc2. The discrepancy between the in vivo essential role of NFATc1 and the in vitro effect of NFATc2 was attributed to selective autoregulation of the NFATc1 gene by NFAT through its promoter region. This suggested that an epigenetic mechanism contributes to the essential function of NFATc1 in cell lineage commitment. Thus, this study establishes that NFATc1 represents a potential therapeutic target for bone disease and reveals a mechanism that underlies the essential role of NFATc1 in bone homeostasis.", 
"A cell undergoes many genetic and epigenetic changes as it transitions to malignancy. Malignant transformation is also accompanied by a progressive loss of tissue homeostasis and perturbations in tissue architecture that ultimately culminates in tumor cell invasion into the parenchyma and metastasis to distant organ sites. Increasingly, cancer biologists have begun to recognize that a critical component of this transformation journey involves marked alterations in the mechanical phenotype of the cell and its surrounding microenvironment. These mechanical differences include modifications in cell and tissue structure, adaptive force-induced changes in the environment, altered processing of micromechanical cues encoded in the extracellular matrix (ECM), and cell-directed remodeling of the extracellular stroma. Here, we review critical steps in this force journey, including mechanical contributions to tissue dysplasia, invasion of the ECM, and metastasis. We discuss the biophysical basis of this force journey and present recent advances in the measurement of cellular mechanical properties in vitro and in vivo. We end by describing examples of molecular mechanisms through which tumor cells sense, process and respond to mechanical forces in their environment. While our understanding of the mechanical components of tumor growth, survival and motility remains in its infancy, considerable work has already yielded valuable insight into the molecular basis of force-dependent tumor pathophysiology, which offers new directions in cancer chemotherapeutics.", 
"The balance of histone acetylation and deacetylation is an epigenetic layer with a critical role in the regulation of gene expression, Histone acetylation induced by histone acetyl transferases (HATs) is associated with gene transcription, while histone hypoacetylation induced by histone deacetylase (HDAC) activity is associated with gene silencing. Altered expression and mutations of genes that encode HDACs have been linked to tumor development since they both induce the aberrant transcription of key genes regulating important cellular functions such as cell proliferation, cell-cycle regulation and apoptosis. Thus, HDACs are among the most promising therapeutic targets for cancer treatment, and they have inspired researchers to study and develop HDAC inhibitors. (C) 2007 Federation of European Biochemical Societies. Published by Elsevier B.V. All rights reserved.", 
"Early developmental perturbations have been linked to adult-onset prostate pathology, including excessive exposure to estrogenic compounds; however, the molecular basis for this imprinting event is not known. An important and controversial health concern is whether low-dose exposures to hormonally active environmental estrogens, such as bisphenol A, can promote human diseases, including prostate cancer. Here, we show that transient developmental exposure of rats to low, environmentally relevant doses of bisphenol A or estradiol increases prostate gland susceptibility to adult-onset precancerous lesions and hormonal carcinogenesis. We found permanent alterations in the DNA methylation patterns of multiple cell signaling genes, suggesting an epigenetic basis for estrogen imprinting. For phosphodiesterase type 4 variant 4 (PDE4D4), an enzyme responsible for cyclic AMP breakdown, a specific methylation cluster was identified in the 5'-flanking CpG island that was gradually hypermethylated with aging in normal prostates, resulting in loss of gene expression. Early and prolonged hypomethylation at this site following neonatal estradiol or bisphenol A exposure resulted in continued, elevated PDE4D4 expression. Cell line studies confirmed that site-specific methylation is involved in transcriptional silencing of the PDE4D4 gene and showed hypomethylation of this gene in prostate cancer cells. Importantly, the PDE4D4 alterations in the estrogen-exposed prostates were distinguishable before histopathologic changes of the gland, making PDE4D4 a candidate molecular marker for prostate cancer risk assessment as a result of endocrine disruptors. In total, these findings indicate that low-dose exposures to ubiquitous environmental estrogens affect the prostate epigenome during development and, in so doing, promote prostate disease with aging.", 
"Resistance to alkylating agents via direct DNA repair by O-6-methylguanine methyltransferase (MGMT) remains a significant barrier to the successful treatment of patients with malignant glioma. The relative expression of MGMT in the tumor may determine response to alkylating agents, and epigenetic silencing of the MGMT gene by promoter methylation plays an important role in regulating MGMT expression in gliomas. MGMT promoter methylation is correlated with improved progression-free and overall survival in patients treated with alkylating agents. Strategies to overcome MGMT-mediated chemoresistance are being actively investigated. These include treatment with nontoxic pseudosubstrate inhibitors of MGMT, such as O6-benzylguanine, or RNA interference-mediated gene silencing of MGMT. However, systemic application of MGMT inhibitors is limited by an increase in hematologic toxicity. Another strategy is to deplete MGMT activity in tumor tissue using a dose-dense temozolomide schedule. These alternative schedules are well tolerated; however, it remains unclear whether they are more effective than the standard dosing regimen or whether they effectively deplete MGMT activity in tumor tissue. Of note, not all patients with glioblastoma having MGMT promoter methylation respond to alkylating agents, and even those who respond will inevitably experience relapse. Herein we review the data supporting MGMT as a major mechanism of chemotherapy resistance in malignant gliomas and describe ongoing studies that are testing resistance-modulating strategies.", 
"MicroRNAs (miR) show characteristic expression signatures in various cancers and can profoundly affect cancer cell behavior. We carried out miR expression profiling of human glioblastoma specimens versus adjacent brain devoid of tumor. This revealed several significant alterations, including a pronounced reduction of miR-128 in tumor samples. miR-128 expression significantly reduced glioma cell proliferation in vitro and glioma xenograft growth in vivo. miR-128 caused a striking decrease in expression of the Bmi-1 oncogene, by direct regulation of the Bmi-1 mRNA 3'-untranslated region, through a single miR-128 binding site. In a panel of patient glioblastoma specimens, Bmi-1 expression was significantly up-regulated and miR-128 was down-regulated compared with normal brain. Bmi-1 functions in epigenetic silencing of certain genes through epigenetic chromatin modification. We found that miR-128 expression caused a decrease in histone methylation (H3K27me(3)) and Akt phosphorylation, and up-regulation of p21(CIP1) levels, consistent with Bmi-1 down-regulation. Bmi-1 has also been shown to promote stem cell self-renewal; therefore, we investigated the effects of miR-128 overexpression in human glioma neurosphere cultures, possessing features of glioma stem-like cells. This showed that miR-128 specifically blocked glioma self-renewal consistent with Bmi-1 down-regulation. This is the first example of specific regulation by a miR of a neural stem cell self-renewal factor, implicating miRs that may normally regulate brain development as important biological and therapeutic targets against the stem cell-like characteristics of glioma. [Cancer Res 2008;68(22):9125-30]", 
"Compelling evidence suggests that Foxp3-expressing CD25(+)CD4(+) regulatory T cells (Treg) are generated within the thymus as a separate lineage. However, Foxp3(+)CD4(+) Treg can also be generated de novo in a TGF-beta-dependent process from naive T cells by TCR triggering. Recently, we have shown that naturally occurring, but not in vitro TGF-beta-induced Foxp3(+) Treg display stable Foxp3 expression that was associated with selective demethylation of an evolutionarily conserved element within the Foxp3 locus named TSDR (Treg-specific demethylated region). Here, we report that inhibition of DNA methylation by azacytidine, even in absence of exogenous TGF-beta, not only promoted de novo induction of Foxp3 expression during priming, but also conferred stability of Foxp3 expression upon restimulation. Most notably, such stable Foxp3 expression was found only for cells displaying enhanced TSDR demethylation. In contrast, in vitro TSDR methylation diminished its transcriptional activity. Foxp3(+) Treg generated in vivo by DEC-205-mediated targeting of agonist ligands to dendritic cells showed long-term survival in the absence of the inducing antigen and exhibited efficient TSDR demethylation. Together, our data suggest that TSDR is an important methylation-sensitive element regulating Foxp3 expression and demonstrate that epigenetic imprinting in this region is critical for establishment of a stable Treg lineage.", 
"WNT signals are transduced to the canonical pathway for cell fate determination, and to the noncanonical pathway for control of cell movement and tissue polarity. Canonical WNTsignals are transduced through Frizzled family receptors and LRP5/LRP6 coreceptor to the beta-catenin signaling cascade. Microtubule affinity-regulating kinase (PAR-1) family kinases, casein kinase le (CKl epsilon), and FRAT are positive regulators of the canonical WNT pathway, whereas APC, AXIN1, AXIN2, CKl alpha, NKD1, NKD2, beta TRCP1, beta TRCP2, ANKRD6, Nemo-like kinase (NLK), and peroxisome proliferator-activated receptor gamma (PPAR gamma) are negative regulators. Nuclear complex, consisting of T-cell factor/lymphoid enhancer factor, p-catenin, BCL9/BCL9L, and PYGO, activates transcription of canonical WNT target genes such as FGF20, DKK1, WISP1 MYC, CCND1, and Glucagon (GCG). Noncanonical WNTsignals are transduced through Frizzled family receptors and ROR2/RYK coreceptors to the Dishevelled-dependent (Rho family GTPases and c-jun NH(2)-terminal kinase) or the Ca(2+)-dependent (NLK and nuclear factor of activated Tcells) signaling cascades. WNTsignals are context-dependently transduced to both pathways based on the expression profile of WNT SFRP, WIF, DKK, Frizzled receptors, coreceptors, and the activity of intracellular WNT signaling regulators. Epigenetic silencing and loss-of-function mutation of negative regulators of the canonical WNT pathway occur in a variety of human cancer. WNT, fibroblast growth factor (FGF), Notch, Hedgehog, and transforming growth factor beta/bone morphogenetic protein signaling network are implicated in the maintenance of tissue homeostasis by regulating self-renewal of normal stem cells as well as proliferation or differentiation of progenitor (transit-amplifying) cells. Breakage of the stem cell signaling network leads to carcinogenesis. Nonsteroidal anti-inflammatory drugs and PPAR gamma agonists with the potential to inhibit the canonical WNT signaling pathway are candidate agents for chemoprevention. ZTM000990 and PKF118-310 are lead compounds targeted to the canonical WNT signaling cascade. Anti-WNT1 and anti-WNT2 monoclonal antibodies show in vitro effects in cancer treatment. After the optimization, derivatives of small-molecule compound and human monoclonal antibody targeted to the WNT signaling pathway could be used in cancer medicine.", 
"Cellular transformation and tumor development result from an accumulation Of mutational and epigenetic changes that alter normal cell growth and survival pathways. For the last 100 years, there has been a vigorous debate (is to whether the unmanipulated immune system can detect and eliminate such altered host derived cells despite the fact that cancer cells frequently express either abnormal proteins or abnormal levels of normal cellular proteins that function as tumor antigens. In this review, toe discuss the current state of this argument and point out some of the recent key experiments demonstrating that immunity not only protects the host from cancer development (i.e., provides a cancer immunosurveillance but also can promote tumor growth, sometimes by generating more aggressive tumors. The terminology cancer immunoediting has been used to describe this dual host protective and tumor promoting action Of immunity, and herein we summarize the ever-increasing experimental and clinical data that support the validity of this concept.", 
"The transcription factor FOXP3 is critical for development and function of regulatory T cells (Treg). Their number and functioning appears to be crucial in the prevention of autoinmumity and allergy, but also to be a negative prognostic marker for various solid tumors. Although expression of the transcription factor FOXP3 currently constitutes the best-known marker for Treg, in humans, transient expression is also observed in activated non-Treg. Extending our recent findings for the murine foxp3 locus, we observed epigenetic modification of several regions in the human FOXP3 locus exclusively occurring in Treg. Importantly, activated conventional CD4(+) T cells and TGF-beta-treated cells displayed no FOXP3 DNA demethylation despite expression of FOXP3, whereas subsets of Treg stable even upon extended in vitro expansion remained demethylated. To investigate whether a whole set of genes might be epigenetically imprinted in the Treg lineage, we conducted a genome-wide differential methylation hybridization analysis. Several genes were found displaying differential methylation between Treg and conventional T cells, but none beside FOXP3 turned out to be entirely specific to Treg when tested on a broad panel of cells and tissues. We conclude that FOXP3 DNA demethylation constitutes the most reliable criterion for natural Treg available at present.", 
"Naive CD4(+) T cells give rise to T-helper-cell subsets with functions that are tailored to their respective roles in host defence. The specification of T-helper-cell subsets is controlled by networks of lineage-specifying transcription factors, which bind to regulatory elements in genes that encode cytokines and other transcription factors. The nuclear context in which these transcription factors act is affected by epigenetic processes, which allow programmes of gene expression to be inherited by progeny cells that at the same time retain the potential for change in response to altered environmental signals. In this Review, we describe these epigenetic processes and discuss how they collaborate to govern the fate and function of T helper cells.", 
"Helper T cells coordinate immune responses through the production of cytokines. Th2 cells express the closely linked 114, 1113, and 115 cytokine genes, whereas these same genes are silenced in the Th1 lineage. The Th1/Th2 lineage choice has become a textbook example for the regulation of cell differentiation, and recent discoveries have further refined and expanded our understanding of how Th2 differentiation is initiated and reinforced by signals from antigen-presenting cells and cytokine-driven feedback loops. Epigenetic changes that stabilize the active or silent state of the 114 locus in differentiating helper T cells have been a major focus of recent research. Overall, the field is progressing toward an integrated model of the signaling and transcription factor networks, cis-regulatory elements, epigenetic modifications, and RNA interference mechanisms that converge to determine the lineage fate and gene expression patterns of differentiating helper T cells.", 
"There has been considerable progress in the systemic treatment of cancer because of the rapid development and clinical application of molecular targeted agents. Although patients with a particular type and stage of cancer are often treated as a single group, more-specific therapy is being considered, as subsets of these patients who are more likely to benefit from treatment with particular agents are being identified. We previously introduced the concept of 'oncogene addiction' to explain how some cancers that contain multiple genetic, epigenetic, and chromosomal abnormalities are dependent on or 'addicted' to one or a few genes for both maintenance of the malignant phenotype and cell survival. Thus, reversal of only one or a few of these abnormalities can inhibit cancer cell growth and in some cases translate to improved survival rates. This review summarizes current experimental and clinical evidence for the concept of oncogene addiction and describes molecular mechanisms that may explain this phenomenon. In addition, we discuss how high-throughput screening methods, including gene-expression profiling and proteomics, and emerging methods for analyzing complex cellular networks can be used to identify the state of oncogene addiction, i.e. the 'Achilles' heel,' in specific cancers. Finally, we discuss the use of molecular targeted agents in combination with other anticancer agents as a strategy to optimize therapy and prevent disease recurrence.", 
"Acetylation is a key posttranslational modification of many proteins responsible for regulating critical intracellular pathways. Although histones are the most thoroughly studied of acetylated protein substrates, histone acetyltransferases (HATs) and deacetylases (HDACs) are also responsible for modifying the activity of diverse types of nonhistone proteins, including transcription factors and signal transduction mediators. HDACs have emerged as uncredentialed molecular targets for the development of enzymatic inhibitors to treat human cancer, and six structurally distinct drug classes have been identified with in vivo bioavailability and intracellular capability to inhibit many of the known mammalian members representing the two general types of NAD+-independent yeast HDACs, Rpd3 (HDACs 1, 2, 3, 8) and Hda1 (HDACs 4,5, 6, 7, 9a, 9b, 10). Initial clinical trials indicate that HDAC inhibitors from several different structural classes are very well tolerated and exhibit clinical activity against a variety of human malignancies; however, the molecular basis for their anticancer selectivity remains largely unknown. HDAC inhibitors have also shown preclinical promise when combined with other therapeutic agents, and innovative drug delivery strategies, including liposome encapsulation, may further enhance their clinical development and anticancer potential. An improved understanding of the mechanistic role of specific HDACs in human tumorigenesis, as well as the identification of more specific HDAC inhibitors, will likely accelerate the clinical development and broaden the future scope and utility of HDAC inhibitors for cancer treatment.", 
"Altered expression of microRNA (miRNA) is strongly implicated in cancer, and recent studies have shown that, in cancer, expression of some miRNAs cells is silenced in association with CpG island hypermethylation. To identify epigenetically silenced miRNAs in colorectal cancer (CRC), we screened for miRNAs induced in CRC cells by 5-aza-2'-deoxycytidine (DAC) treatment or DNA methyltransferase knockout. We found that miRNA-34b (miR-34b) and miR-34c, two components of the p53 network, are epigenetically silenced in CRC; that this down-regulation of miR-34b/c is associated with hypermethylation of the neighboring CpG island; and that DAC treatment rapidly restores miR-34b/c expression. Methylation of the miR-34b/c CpG island was frequently observed in CRC cell lines (nine of nine, 100%) and in primary CRC tumors (101 of 111, 90%), but not in normal colonic mucosa. Transfection of precursor miR-34b or miR-34c into CRC cells induced dramatic changes in the gene expression profile, and there was significant overlap between the genes down-regulated by miR-34b/c and those down-regulated by DAC. We also found that the miR-34b/c CpG island is a bidirectional promoter which drives expression of both miR-34b/c and B-cell translocation gene 4 (BTG4); that methylation of the CpG island is also associated with transcriptional silencing of BTG4; and that ectopic expression of BTG4 suppresses colony formation by CRC cells. Our results suggest that miR-34b/c and BTG4 are novel tumor suppressors in CRC and that the miR-34b/c CpG island, which bidirectionally regulates miR-34b/c and BTG4, is a frequent target of epigenetic silencing in CRC.", 
"The cytosine analogues 5-azacytosine (azacytidine) and 2'-deoxy-5-azacytidine (decitabine) are the currently most advanced drugs for epigenetic cancer therapies. These compounds function as DNA methyltransferase inhibitors and have shown substantial potency in reactivating epigenctically silenced tumor suppressor genes in vitro. However, it has been difficult to define the mode of action of these drugs in patients and it appears that clinical responses are influenced both by epigenetic alterations and by apoptosis induction. To maximize the clinical efficacy of azacytidine and decitabine it will be important to understand the molecular changes induced by these drugs. In this review, we examine the pharmacological properties of azanucleosides and their interactions with various cellular pathways. Because azacytidine and decitabine are prodrugs, an understanding of the cellular mechanisms mediating transmembrane transport and metabolic activation will be critically important for optimizing patient responses. We also discuss the mechanism of DNA methyltransferase inhibition and emphasize the need for the identification of predictive biomarkers for the further advancement of epigenetic therapies. (C) 2008 Wiley-Liss, Inc.", 
"Context Changes over time in epigenetic marks, which are modifications of DNA such as by DNA methylation, may help explain the late onset of common human diseases. However, changes in methylation or other epigenetic marks over time in a given individual have not yet been investigated. Objectives To determine whether there are longitudinal changes in global DNA methylation in individuals and to evaluate whether methylation maintenance demonstrates familial clustering. Design, Setting, and Participants We measured global DNA methylation by luminometric methylation assay, a quantitative measurement of genome- wide DNA methylation, on DNA sampled at 2 visits on average 11 years apart in 111 individuals from an Icelandic cohort ( 1991 and 2002- 2005) and on average 16 years apart in 126 individuals from a Utah sample ( 1982- 1985 and 1997- 2005). Main Outcome Measure Global methylation changes over time. Results Twenty- nine percent of Icelandic individuals showed greater than 10% methylation change over time ( P <. 001). The family- based Utah sample also showed intra-individual changes over time, and further demonstrated familial clustering of methylation change ( P=. 003). The family showing the greatest global methylation loss also demonstrated the greatest loss of gene- specific methylation by a separate methylation assay. Conclusion These data indicate that methylation changes over time and suggest that methylation maintenance may be under genetic control.", 
"The ubiquitous transcription factor Yin Yang 1 (YY1) is known to have a fundamental role in normal biologic processes such as embryogenesis, differentiation, replication, and cellular proliferation. YY1 exerts its effects on genes involved in these processes via its ability to initiate, activate, or repress transcription depending upon the context in which it binds. Mechanisms of action include direct activation or repression, indirect activation or repression via cofactor recruitment, or activation or repression by disruption of binding sites or conformational DNA changes. YY1 activity is regulated by transcription factors and cytoplasmic proteins that have been shown to abrogate or completely inhibit YY1-mediated activation or repression; however, these mechanisms have not yet been fully elucidated. Since expression and function of YY1 are known to be intimately associated with progression through phases of the cell cycle, the physiologic significance of YY1 activity has recently been applied to models of tumor biology. The majority of the data are consistent with the hypothesis that YY1 overexpression and/or activation is associated with unchecked cellular proliferation, resistance to apoptotic stimuli, tumorigenesis and metastatic potential. Studies involving hemato-poetic tumors, epithelial-based tumors, endocrine organ malignancies, hepatocellular carcinoma, and retinoblastoma support this hypothesis. Molecular mechanisms that have been investigated include YY1-mediated downregulation of p53 activity, interference with poly-ADP-ribose polymerase, alteration in c-myc and nuclear factor-kappa B (NF-kappa B) expression, regulation of death genes and gene products, and differential YY1 binding in the presence of inflammatory mediators. Further, recent findings implicate YY1 in the regulation of tumor cell resistance to chemotherapeutics and immune-mediated apoptotic stimuli. Taken together, these findings provide strong support of the hypothesis that YY1, in addition to its regulatory roles in normal biologic processes, may possess the potential to act as an initiator of tumorigenesis and may thus serve as both a diagnostic and prognostic tumor marker; furthermore, it may provide an effective target for antitumor chemotherapy and/or immunotherapy.", 
"Many chemotherapy regiments are successfully used to treat breast cancer; however, often breast cancer cells develop drug resistance that usually leads to a relapse and worsening of prognosis. We have shown recently that epigenetic changes such as DNA methylation and histone modifications play an important role in breast cancer cell resistance to chemotherapeutic agents. Another mechanism of gene expression control is mediated via the function of small regulatory RNA, particularly microRNA (miRNA); its role in cancer cell drug resistance still remains unexplored. In the present study, we investigated the role of miRNA in the resistance of human MCF-7 breast adenocarcinoma cells to doxorubicin (DOX). Here, we for the first time show that DOX-resistant MCF-7 cells (MCF-7/DOX) exhibit a considerable dysregulation of the miRNAome profile and altered expression of miRNA processing enzymes Dicer and Argonaute 2. The mechanistic link of miRNAome deregulation and the multidrug-resistant phenotype of MCF-7/DOX cells was evidenced by a remarkable correlation between specific miRNA expression and corresponding changes in protein levels of their targets, specifically those ones that have a documented role in cancer drug resistance. Furthermore, we show that microRNA-451 regulates the expression of multidrug resistance 1 gene. More importantly, transfection of the MCF-7/DOX-resistant cells with microRNA-451 resulted in the increased sensitivity of cells to DOX, indicating that correction of altered expression of miRNA may have significant implications for therapeutic strategies aiming to overcome cancer cell resistance.", 
"In the last few years, microRNAs (miRNA) have started a revolution in molecular biology and emerged as key players in the carcinogenesis. They have been identified in various tumor types, showing that different sets of miRNAs are usually deregulated in different cancers. To identify the miRNA signature that was specific for oral squamous cell carcinoma (OSCC), we first examined expression profiles of 148 miRNAs in a panel of 18 OSCC cell lines and the immortalized oral keratinocyte line RT7 as a control. Compared with RT7, the expression of 54 miRNAs (36.5%) was frequently down-regulated in OSCC lines (<0.5-fold expression, >= 66.7% of 18 lines). Among these 54 miRNAs, we further analyzed four of these miRNAs (i.e., miR-34b, miR-137, miR-193a, and miR-203), located around CpG islands, to identify tumor-suppressive miRNAs silenced through aberrant DNA methylation. The expression of those four genes was restored by treatment with 5-aza-2'-deoxycytidine in OSCC cells lacking their expression, In addition, expression levels of the four miRNAs were inversely correlated with their DNA methylation status in the OSCC lines. In primary tumors of OSCC with paired normal oral mucosa, down-regulation of miRNA expression through tumor-specific hypermethylation was more frequently observed for miR-137 and miR-193a than for miR-34b and miR-203. Moreover, the ectopic transfection of miR-137 or miR-193a into OSCC lines lacking their expressions significantly reduced cell growth, with down-regulation of the translation of cyclin-dependent kinase 6 or E2F transcription factor 6, respectively. Taken together, our results clearly show that miR-137 and miR-193a are tumor suppressor miRNAs epigenetically silenced during oral carcinogenesis.", 
"Intrauterine growth retardation (IUGR) has been linked to the onset of diseases in adulthood, including type 2 diabetes, and has been proposed to result from altered gene regulation patterns due to epigenetic modifications of developmental genes. To determine whether epigenetic modifications may play a role in the development of adult diabetes following IUGR, we used a rodent model of IUGR that expresses lower levels of Pdx1, a pancreatic and duodenal homeobox 1 transcription factor critical for 0 cell function and development, which develops diabetes in adulthood. We found that expression of Pdx1 was permanently reduced in IUGR beta cells and underwent epigenetic modifications throughout development. The fetal IUGR state was characterized by loss of USF-1 binding at the proximal promoter of Pdx1, recruitment of the histone deacetylase 1 (HDAC1) and the corepressor Sin3A, and deacetylation of histones H3 and H4. Following birth, histone 3 lysine 4 (H3K4) was demethylated and histone 3 lysine 9 (H3K9) was methylated. During the neonatal period, these epigenetic changes and the reduction in Pdx1 expression could be reversed by HDAC inhibition. After the onset of diabetes in adulthood, the CpG island in the proximal promoter was methylated, resulting in permanent silencing of the Pdx1 locus. These results provide insight into the development of type 2 diabetes following IUGR and we believe they are the first to describe the ontogeny of chromatin remodeling in vivo from the fetus to the onset of disease in adulthood.", 
"The epidemic of obesity took off from about 1980 and in almost all countries has been rising inexorably ever since. Only in 1997 did WHO accept that this was a major public health problem and, even then, there was no accepted method for monitoring the problem in children. It was soon evident, however, that the optimum population body mass index is about 21 and this is particularly true in Asia and Latin America where the populations are very prone to developing abdominal obesity, type 2 diabetes and hypertension. These features are now being increasingly linked to epigenetic programming of gene expression and body composition in utero and early childhood, both in terms of fat/lean tissue ratios and also in terms of organ size and metabolic pathway regulation. New Indian evidence suggests that insulin resistance at birth seems linked to low birth weight and a higher proportion of body fat with selective B12 deficiency and abnormalities of one carbon pool metabolism potentially responsible and affecting 75% of Indians and many populations in the developing world. Biologically there are also adaptive biological mechanisms which limit weight loss after weight gain and thereby in part account for the continuing epidemic despite the widespread desire to slim. Logically, the burden of disease induced by inappropriate diets and widespread physical inactivity can be addressed by increasing physical activity (PA), but simply advocating more leisure time activity is unrealistic. Substantial changes in urban planning and diet are needed to counter the removal of any every day need for PA and the decades of misdirected food policies which with free market forces have induced our current 'toxic environment'. Counteracting this requires unusual policy initiatives.", 
"Environmental effects on the materno-foetal interaction determine birth outcomes that predict health over the lifespan. Thus, maternal undernutrition or stress associate with low birth weight, leading to an increased risk of metabolic and cardiovascular illness in the offspring. We argue that these effects are, in part, mediated by direct and indirect effects on the hypothalamic-pituitary-adrenal (HPA) axis such that (i) the effect of maternal adversity on foetal growth is mediated by adrenal glucocorticoids and (ii) environmental adversity alters maternal physiology and behaviour, which then programs HPA activity in the offspring.", 
"While cisplatin and carboplatin are active versus most common cancers, epithelial malignancies are incurable when metastatic. Even if an initial response occurs, acquired resistance due to mutations and epigenetic events limits efficacy. Resistance may be due to excess of a resistance factor, to saturation of factors required for tumor cell killing, or to mutation or alteration of a factor required for tumor cell killing. Platinum resistance could arise from decreased tumor blood flow, extracellular conditions, reduced platinum uptake, increased efflux, intracellular detoxification by glutathione, etc., decreased binding (e.g., due to high intracellular pH), DNA repair, decreased mismatch repair, defective apoptosis, antiapoptotic factors, effects of several signaling pathways, or presence of quiescent non-cycling cells. In lung cancer, flattening of dose-response Curves at higher doses suggests that efficacy is limited by exhaustion of something required for cell killing, and several clinical observations suggest epigenetic events may play a major role in resistance. (c) 2007 Elsevier Ireland Ltd. All rights reserved.", 
"We are in an era where the potential exists for deriving comprehensive profiles of DNA alterations characterizing each form of human cancer. Such profiles would provide invaluable insight into mechanisms underlying the evolution of each tumor type and will provide molecular markers, which could radically improve cancer detection. To date, no one type of DNA change has been defined which accomplishes this purpose. Herein, by using a candidate gene approach, we shaw that one category of DNA alteration, aberrant methylation of gene promoter regions, can enormously contribute to the above goals. We have now analyzed a series of promoter hypermethylation changes in 12 genes (p16(INK4a), p15(INK4b), p14(ARF), p73, APC(5), BRCA1, hMLH1, GSTP1, MGMT, CDH1, TIMP3, and DAPK) each rigorously characterized for association with abnormal gene silencing in cancer, in DNA from over 600 primary tumor samples representing 15 major tumor types. The genes play known important roles in processes encompassing tumor suppression, cell cycle regulation, apoptosis, DNA repair, and metastastic potential. A unique profile of promoter hypermethylation exists for each human cancer in which some gene changes are shared and others are cancer-type specific. The hypermethylatian of the genes occurs independently to the extent that a panel of three to four markers defines an abnormality in 70-90% of each cancer type. Our results provide an unusual view of the pervasiveness of DNA alterations, in this case an epigenetic change, in human cancer and a powerful set of markers to outline the disruption of critical pathways in tumorigenesis and for derivation of sensitive molecular detection strategies for virtually every human tumor type.", 
"Since its discovery in 1983, the epigenetics of human cancer has been in the shadows of human cancer genetics. But this area has become increasingly visible with a growing understanding of specific epigenetic mechanisms and their role in cancer, including hypomethylation, hypermethylation, loss of imprinting and chromatin modification. This timeline traces the field from its conception to the present day. It also addresses the genetic basis of epigenetic changes - an emerging area that promises to unite cancer genetics and epigenetics, and might serve as a model for understanding the epigenetic basis of human disease more generally.", 
"The past few years have seen an explosion of interest in the epigenetics of cancer. This has been a consequence of both the exciting coalescence of the chromatin and DNA methylation fields, and the realization that DNA methylation changes are involved in human malignancies. The ubiquity of DNA methylation changes has opened the way to a host of innovative diagnostic and therapeutic strategies. Recent advances attest to the great promise of DNA methylation markers as powerful future tools in the clinic.", 
"Cancer-associated DNA hypomethylation is as prevalent as cancer-linked hypermethylation, but these two types of epigenetic abnormalities usually seem to affect different DNA sequences. Much more of the genome is generally subject to undermethylation rather than overmethylation. Genomic hypermethylation in cancer has been observed most often in CpG islands in gene regions. In contrast, very frequent hypomethylation is seen in both highly and moderately repeated DNA sequences in cancer, including heterochromatic DNA repeats, dispersed retrotransposons, and endogenous retroviral elements. Also, unique sequences, including transcription control sequences, are often subject to cancer-associated undermethylation. The high frequency of cancer-linked DNA hypomethylation, the nature of the affected sequences, and the absence of associations with DNA hypermethylation are consistent with an independent role for DNA undermethylation in cancer formation or tumor progression. Increased karyotypic instability and activation of tumor-promoting genes by cis or trans effects, that might include altered heterochromatin-euchromatin interactions, may be important consequences of DNA hypomethylation which favor oncogenesis. The relationship of DNA hypomethylation to tumorigenesis is important to be considered in the light of cancer therapies involving decreasing DNA methylation. Inducing DNA hypomethylation may have short-term anticancer effects, but might also help speed tumor progression from cancer cells surviving the DNA demethylation chemotherapy.", 
"5-Azacytidine was first synthesized almost 40 years ago. It was demonstrated to have a wide range of anti-metabolic activities when tested against cultured cancer cells and to be an effective chemotherapeutic agent for acute myelogenous leukemia. However, because of 5-azacytidine's general toxicity, other nucleoside analogs were favored as therapeutics. The finding that 5-azacytidine was incorporated into DNA and that, when present in DNA, it inhibited DNA methylation, led to widespread use of 5-azacytidine and 5-aza-2'-deoxycytidine (Decitabine) to demonstrate the correlation between loss of methylation in specific gene regions and activation of the associated genes. There is now a revived interest in the use of Decitabine as a therapeutic agent for cancers in which epigenetic silencing of critical regulatory genes has occurred. Here, the current status of our understanding of the mechanism(s) by which 5-azacytosine residues in DNA inhibit DNA methylation is reviewed with an emphasis on the interactions of these residues with bacterial and mammalian DNA (cytosine-C5) methyltransferases. The implications of these mechanistic studies for development of less toxic inhibitors of DNA methylation are discussed.", 
"We have come a long way since the first reports of the existence of aberrant DNA methylation in human cancer. Hypermethylation of CpG islands located in the promoter regions of tumor suppressor genes is now firmly established as an important mechanism for gene inactivation. CpG island hypermethylation has been described in almost every tumor type. Many cellular pathways are inactivated by this type of epigenetic lesion: DNA repair (hMLH1, MGMT), cell cycle (p16(INK4a), p15(INK4b), p14(ARF)), apoptosis (DAPK), cell adherence (CDH1, CDH13), detoxification (GSTP1), etc... However, we still know little of the mechanisms of aberrant methylation and why certain genes are selected over others. Hypermethylation is not an isolated layer of epigenetic control, but is linked to the other pieces of the puzzle such as methyl-binding proteins, DNA methyltransferases and histone deacetylase, but our understanding of the degree of specificity of these epigenetic layers in the silencing of specific tumor suppressor genes remains incomplete. The explosion of user-friendly technologies has given rise to a rapidly increasing list of hypermethylated genes. Careful functional and genetic studies are necessary to determine which hypermethylation events are truly relevant for human tumorigenesis. The development of CpG island hypermethylation profiles for every form of human tumors has yielded valuable pilot clinical data in monitoring and treating cancer patients based in our knowledge of DNA methylation. Basic and translational will both be needed in the near future to fully understand the mechanisms, roles and uses of CpG island hypermethylation in human cancer. The expectations are high.", 
"DNA methylation is an important regulator of gene transcription, and its role in carcinogenesis has been a topic of considerable interest in the last few years. Alterations in DNA methylation are common in a variety of tumors as well as in development. Of all epigenetic modifications, hypermethylation, which represses transcription of the promoter regions of tumor suppressor genes leading to gene silencing, has been most extensively studied. However, global hypomethylation has also been recognized as a cause of oncogenesis. New information concerning the mechanism of methylation and its control has led to the discovery of many regulatory proteins and enzymes. The contribution of dietary folate and methylene terahydrofolate reductase polymorphisms to methylation patterns in normal and cancer tissues is under intense investigation. As methylation occurs early and can be detected in body fluids, it may be of potential use in early detection of tumors and for determining the prognosis. Because DNA methylation is reversible, drugs like 5'-azacytidine, decitabine, and histone deacetylase inhibitors are being used to treat a variety of tumors. Novel demethylating agents such as antisense DNA methyl transferase and small interference RNA are being developed, making the field of DNA methylation wider and more exciting. (C) 2004 by American Society of Clinical Oncology.", 
"The role of DNA methylation and of the maintenance DNA methyltransferase Dnmt1 in the epigenetic regulation of developmental stage- and cell lineage-specific gene expression in vivo is uncertain. This is addressed here through the generation of mice in which Dnmt1 was inactivated by Cre/loxP-mediated deletion at sequential stages of T cell development. Deletion of Dnmt1 in early double-negative thymocytes led to impaired survival of TCR alpha beta (+) cells and the generation of atypical CD8(+)TCR gamma delta (+) cells. Deletion of Dnmt1 in double-positive thymocytes impaired activation-induced proliferation but differentially enhanced cytokine mRNA expression by naive peripheral T cells. We conclude that Dnmt1 and DNA methylation are required for the proper expression of certain genes that define fate and determine function in T cells.", 
"DNA hypermethylation in CpG-rich promoters is now recognized as a common feature of human neoplasia. However, the pathophysiology of hypermethylation (why, when, where) remains obscure. Cancers can be classified according to their degree of methylation, and those cancers with high degrees of methylation (the CpG island methylator phenotype, or CIMP) represent a clinically and aetiologically distinct group that is characterized by 'epigenetic instability'. Furthermore, CIMP-associated cancers seem to have a distinct epidemiology, a distinct histology, distinct precursor lesions and distinct molecular features.", 
"The idea that tumors must escape from immune recognition contains the implicit assumption that tumors can be destroyed by immune responses either spontaneously or as the result of immunotherapeutic intervention. Simply put, there is no need for tumor escape without immunological pressure. Here, we review evidence supporting the immune escape hypothesis and critically explore the mechanisms that may allow such escape to occur. We discuss the idea that the central engine for generating immunoresistant tumor cell variants is the genomic instability and dysregulation that is characteristic of the transformed genome. Natural selection of heterogeneous tumor cells results in the survival and proliferation of variants that happen to possess genetic and epigenetic traits that facilitate their growth and immune evasion. Tumor escape variants are likely to emerge after treatment with increasingly effective immunotherapies.", 
"Background: The recently identified RASSF1 locus is located within a 120-kilobase region of chromosome 3p21.3 that frequently undergoes allele loss in lung and breast cancers. We explored the hypothesis that RASSF1 encodes a tumor suppressor gene for lung and breast cancers. Methods: We assessed expression of two RASSF1 gene products, RASSF1A and RASSF1C, and the methylation status of their respective promoters in 27 non-small-cell lung cancer (NSCLC) cell lines, in 107 resected NSCLCs, in 47 small-cell Lung cancer (SCLC) cell lines, in 22 breast cancer cell lines, in 39 resected breast cancers, in 104 nonmalignant lung samples, and in three breast and lung epithelial cultures, We also transfected a lung cancer cell line that lacks RASSF1A expression with vectors containing RASSF1A complementary DNA to determine whether exogenous expression of RASSF1A would affect in vitro growth and in vivo tumorigenicity of this cell line. Ail statistical tests were two-sided. Results: RASSF1A messenger RNA was expressed in nonmalignant epithelial cultures but not in 100% of the SCLC, in 65% of the NSCLC, or in 60% of the breast cancer lines. By contrast, RASSF1C was expressed in all nonmalignant cell cultures and in nearly all cancer cell lines. RASSF1A promoter hypermethylation was detected in 100% of SCLC, in 63% of NSCLC, in 63% of breast cancer lines, in 30% of primary NSCLCs, and in 39% of primary breast tumors but in none of the nonmalignant lung tissues, RASSF1A promoter hypermethylation in resected NSCLCs was associated with impaired patient survival (P =.046), Exogenous expression of RASSF1A in a cell line lacking expression decreased in vitro colony formation and in vivo tumorigenicity. Conclusion: RASSF1A is a potential tumor suppressor gene that undergoes epigenetic inactivation in lung and breast cancers through hypermethylation of its promoter region.", 
"Purpose: In the setting of a prospective clinical trial, we determined the predictive value of the methylation status of the O-6-methylguanine-DNA methyltransferase (MGMT) promoter for outcome in glioblastoma patients treated with the alkylating agent temozolomide. Expression of this excision repair enzyme has been associated with resistance to alkylating chemotherapy. Experimental Design: The methylation status of MGMT in the tumor biopsies was evaluated in 38 patients undergoing resection for newly diagnosed glioblastoma and enrolled in a Phase 11 trial testing concomitant and adjuvant temozolomide and radiation. The epigenetic silencing of the MGMT gene was determined using methylation-specific PCR. Results: Inactivation of the MGMT gene by promoter methylation was associated with longer survival (P = 0.0051; Log-rank test). At 18 months, survival was 62% (16 of 26) for patients testing positive for a methylated MGMT promoter but reached only 8% (1 of 12) in absence of methylation (P = 0.002; Fisher's exact test). In the presence of other clinically relevant factors, methylation of the MGMT promoter remains the only significant predictor (P = 0.017; Cox regression). Conclusions: This prospective clinical trial identifies MGMT-methylation status as an independent predictor for glioblastoma patients treated with a methylating agent. The association of the epigenetic inactivation of the DNA repair gene MGMT with better outcome in this homogenous cohort may have important implications for the design of future trials and supports efforts to deplete MGMT by O-6-benzylguanine, a noncytotoxic substrate of this enzyme.", 
"The Cyclin D-Cdk4,6/lNK4/Rb/E2F pathway plays a key role in controlling cell growth by integrating multiple mitogenic and antimitogenic stimuli. The components of this pathway are gene families with a high level of structural and functional redundancy and are expressed in an overlapping fashion in most tissues and cell types. Using classical transgenic technology as well as gene-targeting in ES cells, a series of mouse models have been developed to study the in vivo function of individual components of this pathway in both normal homeostasis and tumor development. These models have proven to be useful to define specific as well as redundant roles among members of these cell cycle regulatory gene families. This pathway is deregulated in the vast majority of human tumors by genetic and epigenetic alterations that target at least some of its key members such as Cyclin D1, Cdk4, INK4a and INK4b, pRb etc. As a consequence, some of these molecules are currently being considered as targets for cancer therapy, and several novel molecules, such as Cdk inhibitors, are under development as potential anti-cancer drugs. (C) 2002 Elsevier Science B.V. All rights reserved.", 
"Given the vast number of genetic and epigenetic changes associated with carcinogenesis, it is clear that tumors express many neoantigens. A central question in cancer immunology is whether recognition of tumor antigens by the immune system leads to activation (i.e., surveillance) or tolerance. Paradoxically, while strong evidence exists that specific immune surveillance systems operate at early stages of tumorigenesis, established tumors primarily induce immune tolerance. A unifying hypothesis posits that the fundamental processes of cancer progression, namely tissue invasion and metastasis, are inherently proinflammatory and thus activating for innate and adaptive antitumor immunity. To elude immune surveillance, tumors must develop mechanisms that block the elaboration and sensing of proinflammatory danger signals, thereby shifting the balance from activation to tolerance induction. Elucidation of these mechanisms provides new strategies for cancer immunotherapy.", 
"Cancer is an epigenetic disease at the same level that it can be considered a genetic disease. In fact, epigenetic changes, particularly DNA methylation, are susceptible to change and are excellent candidates to explain how certain environmental factors may increase the risk of cancer. The delicate organization of methylation and chromatin states that regulates the normal cellular homeostasis. of gene expression patterns becomes unrecognizable in the cancer cell. The genome of the transformed cell undergoes simultaneously a global genomic hypomethylation and a dense hypermethylation of the CpG islands associated with gene regulatory regions. These dramatic changes may lead to chromosomal instability, activation of endogenous parasitic sequences, loss of imprinting, illegitimate expression, aneuploidy, and mutations, and may contribute to the transcriptional silencing of tumour suppressor genes. The hypermethylation-associated inactivation affects virtually all of the pathways in the cellular network, such as DNA repair (hMLH1, BRCA1, MGMT,...), the cell cycle (p16(INK4a), p14(ARF), p15(INK4b),...), and apoptosis (DAPK, APAF-1,...). The aberrant CpG island methylation can also be used as a biomarker of malignant cells and as a predictor of their behaviour, and may constitute a good target for future therapies. Copyright (C) 2002 John Wiley Sons, Ltd.", 
"The field of epigenetics has recently moved to the forefront of studies relating to diverse processes such as transcriptional regulation, chromatin structure, genome integrity, and tumorigenesis. Recent work has revealed how DNA methylation and chromatin structure are linked at the molecular level and how methylation anomalies play a direct causal role in tumorigenesis and genetic disease. Much new information has also come to light regarding the cellular methylation machinery, known as the DNA methyltransferases, in terms of their roles in mammalian development and the types of proteins they are known to interact with, This information has forced a new view for the role of DNA methyltransferases. Rather than enzymes that act in isolation to copy methylation patterns after replication, the types of interactions discovered thus far indicate that DNA methyltransferases may be components of larger complexes actively involved in transcriptional control and chromatin structure modulation. These new findings will likely enhance our understanding of the myriad roles of DNA methylation in disease as well as point the may to novel therapies to prevent or repair these defects.", 
"The epigenome is defined by DNA methylation patterns and the associated posttranslational modifications of histones. This histone code determines the expression status of individual genes dependent upon their localization on the chromatin. The silencing of gene expression is associated with deacetylated histones, which are often found to be associated with regions of DNA methylation as well as methylation at the lysine 4 residue of histone 3. In contrast, the activation of gene expression is associated with acetylated histones and methylation at the lysine 9 residue of histone 3. The histone deactylases play a major role in keeping the balance between the acetylated and deacetylated states of chromatin. Histone deacetylases (HDACs) are divided into three classes: class I HDACs (HDACs 1, 2, 3, and 8) are similar to the yeast RPD3 protein and localize to the nucleus; class 11 HDACs (HDACs 4, 5, 6, 7, 9, and 10) are homologous to the yeast HDA1 protein and are found in both the nucleus and cytoplasm; and class III HDACs form a structurally distinct class of NAD-dependent enzymes that are similar to the yeast SIR2 proteins. Since inappropriate silencing of critical genes can result in one or both hits of tumor suppressor gene (TSG) inactivation in cancer, theoretically the reactivation of affected TSGs could have an enormous therapeutic value in preventing and treating cancer. Indeed, several HDAC inhibitors are currently being developed and tested for their potency in cancer chemotherapy. Importantly, these agents are also potentially applicable to chemoprevention if their toxicity can be minimized. Despite the toxic side effects and lack of specificity of some of the inhibitors, progress is being made. With the elucidation of the structures, functions and modes of action of HDACs, finding agents that may be targeted to specific HDACs and potentially reactivate expression of only a defined set of affected genes in cancer will be more attainable.", 
"CpG island hypermethylation is a mechanism of gene silencing that can be usurped by neoplastic cells to inactivate undesirable genes. In the colon, hypermethylation often starts in normal mucosa as a function of age and Is markedly increased in cancer. To test the hypothesis that subjects at increased risk of colon canter have higher levels of methylation in their nonneoplastic mucosa, we studied methylation patterns of five genes in the normal and dysplastic mucosa of patients with ulcerative colitis (UC), a condition associated with a marked increased risk of colon cancer. One gene (Mlh1) was unmethylated in all tissues examined, All four remaining genes had low but detectable levels of methylation in the epithelium of UC patients without evidence of dysplasia, and this methylation was not different from non-UC controls. BS contrast, all four genes were highly methylated in dysplastic epithelium from high-grade dysplasia (HGD)/ cancer patients with UC; methylation in HGD versus controls averaged 40.0% versus 7.4% (P = 0.00003) for ER, 44.0% versus 3.0% (P < 0.00003) for MYOD, 9.4% versus 2.4% (P = 0.03) for p16 exon 1, and 57.5% versus 30.6% (P = 0.01) fur CSPG2, Importantly, three of the four genes were also highly methylated in the normal appearing (nondysplastic) epithelium from these same HGD/cancer patients, indicating that methylation precedes dysplasia and is widespread in these patients. Compared with controls, methylation averaged 20.1% versus 7.2% (P = 0.07) for ER, 18.4% versus 3.0% (P < 0.008) for MYOD, and 7.9% versus 2.4% (P = 0.007) for p16 exon 1. These results are consistent with the hypothesis that age-related methylation marks (and may lead to) the field defect that reflects acquired predisposition to colorectal neoplasia, Furthermore, the data suggest that chronic inflammation is associated with high levels of methylation, perhaps as a result of increased cell turnover, and that UC can be viewed as resulting in premature aging of colorectal epithelial cells.", 
"O-6-Methylguanine DNA methyltransferase (MGMT) is a DNA repair protein that removes mutagenic and cytotoxic adducts from the O-6 position of guanine, O-6-methylguanine mispairs with thymine during replication, and if the adduct is not removed, this results in conversion from a guanine-cytosine pair to an adenine-thymine pair. In vitro assays show that MGMT expression avoids G to A mutations and MGMT transgenic mice are protected against G to A transitions at ras genes. We have recently demonstrated that the MGMT gene is silenced by promoter methylation in many human tumors, including colorectal carcinomas. To study the relevance of defective MGMT function by aberrant methylation in relation to the presence of K-ras mutations, we studied 244 colorectal tumor samples for MGMT promoter hypermethylation and K-ras mutational status. Our results show a clear association between the inactivation of MGMT by promoter hypermethylation and the appearance of G to A mutations at K-ras: 71% (36 of 51) of the tumors displaying this particular type of mutation had abnormal MGMT methylation, whereas only 32% (12 of 37) of those with other K-ras mutations not involving G to A transitions and 35% (55 of 156) of the tumors without R-ras mutations demonstrated MGMT methylation (P = 0.002), In addition, MGMT loss associated with hypermethylation was observed in the small adenomas, including those that do not yet contain K-ras mutations. Hypermethylation of other genes such as p16(INK4 alpha) and p14(ARF) was not associated with either MGMT hypermethylation or K-ras mutation. Our data suggest that epigenetic silencing of MGMT by promoter hypermethylation may Lead to a particular genetic change in human cancer, specifically G to A transitions in the K-ras oncogene.", 
"In children, cancer probably arises from a combination of inherited genetic mutations and genetic alterations that are acquired during the rapid cellular expansion that occurs during embryogenesis, and it is rarely associated with immune cell infiltrates. Conversely, in adults, cancer is frequently preceded by a long period of subclinical inflammatory disease and micronecrosis that provides a setting in which the epigenetic regulation of genes, cell death, cell proliferation and mutagenesis occurs. Here, we provocatively suggest that adult cancer results from rounds of disordered and unscheduled necrotic cell death, subsequent epithelial proliferation and the resulting suppressed immunity, rather than from a process that is dictated solely by cell growth. This paradigm shift regarding the development of cancer and this 'sixth sense' of the immune system indicates new strategies for cancer prevention and therapy.", 
"The INK4a/ARF locus encodes two cell cycle-regulatory proteins, p16(INK4a) and p14(ARF), which share an exon using different reading frames. p14(ARF) antagonizes MDM2-dependent p53 degradation. However, no point mutations in p14(ARF) not altering p16(INK4a) have been described in primary tumors. We report that p14(ARF) is epigenetically inactivated in several colorectal cell lines, and its expression is restored by treatment with demethylating agents. In primary colorectal carcinomas, p14(ARF) promoter hypermethylation was found in 31 of 110 (28%) of the tumors and observed in 13 or 41 (32%) colorectal adenomas but was not present in any normal tissues. p14(ARF) methylation appears in the context of an adjacent unmethylated p16(INK4a) promoter in 16 of 31 (52%) of the carcinomas methylated at p14(ARF). Although p14(ARF) hypermethylation was slightly overrepresented in tumors with wild-type p53 compared to tumors harboring p53 mutations [19 of 55 (34%) versus 12 of 55 (22%)], this difference did not reach statistical significance, p14(ARF) aberrant methylation was not related to the presence of K-ras mutations. Our results demonstrate that p14(ARF) promoter hypermethylation is frequent in colorectal cancer and occurs independently of the p16(INK4a) methylation status and only marginally in relation to the p53 mutational status.", 
"Polycomb group protein Ezh2 is an essential epigenetic regulator of embryonic development in mice, but its role in the adult organism is unknown. High expression of Ezh2 in developing murine lymphocytes suggests Ezh2 involvement in lymphopoiesis. Using Cre-mediated conditional mutagenesis, we demonstrated a critical role for Ezh2 in early B cell development and rearrangement of the immunoglobulin heavy chain gene (Igh). We also revealed Ezh2 as a key regulator of histone H3 methylation in early B cell progenitors. Our data suggest Ezh2-dependent histone H3 methylation as a novel regulatory mechanism controlling Igh rearrangement during early murine B cell development.", 
"Esophageal adenocarcinoma (EAC) arises after normal squamous mucosa undergoes metaplasia to specialized columnar epithelium (intestinal metaplasia or Barrett's esophagus), which can then ultimately progress to dysplasia and subsequent malignancy. Epigenetic studies of this model have thus far been limited to the DNA methylation analysis of a few genes. In this study, we analyzed a panel of 20 genes using a quantitative, high-throughput methylation assay, MethyLight. Ne used this broader approach to gain insight into concordant methylation behavior between genes and to generate epigenomic fingerprints for the different histological stages of EAC. Our study included a total of 104 tissue specimens from 51 patients with different stages of Barrett's esophagus and/or associated adenocarcinoma. We screened 84 of these samples with the full panel of 20 genes and found distinct classes of methylation patterns in the different types of tissue. The most informative genes,were those with an intermediate frequency of significant hypermethylation [ranging from 15% (CDKN2A) to 60% (MGMT) of the samples]. This group could be further subdivided into three classes, according to the absence (CDKN2A, ESRI, and MYODI) or presence (CALCA, MGMT, and TIMP3) of methylation in normal esophageal mucosa and stomach, or the infrequent methylation of normal esophageal mucosa accompanied by methylation in all normal stomach samples (APC). The other genes were less informative, because the frequency of hypermethylation was below 5% (ARF, CDH1, CDKN2B, GSTP1, MLH1, PTGS2, and THBS1), completely absent (CTNNB1, RBI, TGFBR2, and TYMS1), or ubiquitous (H1C1 and MTHFR), regardless of tissue type. Each class undergoes unique epigenetic changes at different steps of disease progression of EAC, suggesting a step-wise loss of multiple protective barriers against CpG island hypermethylation. The aberrant hypermethylation occurs at many different loci in the same tissues, suggestive of an overall deregulation of methylation control in EAC tumorigenesis. However, we did not find evidence for a distinct group of tumors with a CpG island methylator phenotype. Finally,we found that normal and metaplastic tissues from patients with evidence of associated dysplasia or cancer had a significantly higher incidence of hypermethylation than similar tissues from patients with no further progression of their disease. The fact that the samples from these two groups of patients were histologically indistinguishable, yet molecularly distinct, suggests that the occurrence of such hypermethylation may provide a clinical tool to identify patients with premalignant Barrett's who are at risk for further progression.", 
"Promoter hypermethylation is an important. pathway for repression of gene transcription in cancer cells. We analyzed aberrant DNA methylation at four genes in primary tumors from 95 head and neck cancer patients and then used the presence of this methylation as a marker for cancer cell detection in serum DNA, These four genes were tested by ethylation-specific PCR and included: p16 (CDKN2A) O-6-methylguanine-DNA-methyltransferase, glutathione S-transferase P1, and death-associated protein kinase (DAP-kinase), Fifty-five % (52 of 95) of the primary tumors displayed promoter hypermethylation in at least one of the genes studied: 27% (26/95) at p16, 33% (31 of 95) at O-6-methylguanine-DNA-methyltransferase; and 18% (17 of 92) at DAP-kinase. No promoter hypermethylation was observed at the glutathione S-transferase P1 gene promoter. We detected a statistically significant correlation between the presence of DAP-kinase gene promoter hypermethylation and lymph node involvement (P = 0.014) and advanced disease stage (P = 0.016). In 50 patients with paired serum available for epigenetic analysis, the same methylation pattern was detected in the corresponding serum DNA of 21 (42%) cases. Among the patients with methylated serum DNA, 5 developed distant metastasis compared with the occurrence of metastasis in only 1 patient negative for serum promoter hypermethylation (P = 0.056). Promoter hypermethylation of key genes in critical pathways is common in head and neck cancer and represents a promising serum marker for monitoring affected patients.", 
"The base sequence of DNA provides the genetic code for proteins. The regulation of expression or suppression of gene transcription is largely determined by the structure of the chromatin-referred to as epigenetic gene regulation (Agaliori et al., 2002: Jenuwein and Allis, 2001; Richards and Elgin, 2002; Spotswood and Turner, 2002; Zhang and Reinberg, 2001). Posttranslational modifications of the histories of chromatin play an important role in regulating gene expression. Some of the most extensively studied epigenetic modifications involve acetylation/deacetylation of lysines in the tails of the core histones, which is controlled by the action of histone deacetylases (HDACs) and histone aceryltransferases (HATs). A controlled balance between histone acerylation and deacetylation appears to be essential for normal cell growth (Waterborg. 2002). Alterations in the structure or expression of HATs and HDACs occur in many cancers (Jones and Baylin, 2002; Marks et al., 2001, 2003; Timmermann et al.. 2001; Wang et al., 2001). A structurally diverse group of molecules has been developed that can inhibit HDACs (HDACi) (Arts et al., 2003; Bouchain and Delorme, 2003; Curtin and Glaser, 2003; Johnstone and Licht, 2003; Marks et al., 2003, Remiszewski, 2003: Richon e. al., 1998; Yoshida et al., 2003). These inhibitors induce growth arrest, differentiation, and/or apoptosis of cancer cells in vitro and in in vivo tumor-bearing animal models. Clinical trials with several of these agents have shown that certain HDACi have antitumor activity against various cancers at doses that are well tolerated by patients (Gottlicher et al.,. 200 1: Kelly et al., 2002a,b; Piekarz et al., 2001; Wozniak et al.. 1999). (C) 2004 Elsevier Inc.", 
"Silencing of genes by aberrant promoter hypermethylation is now recognized as a crucial component in cancer initiation and progression. Highly sensitive assays have been developed to assess gene-promoter methylation in biological fluids. The detection of methylated genes in sputum could lead to the development of a screening test to non-invasively identify early cancer in high-risk people.", 
"Aberrant DNA methylation patterns may be the earliest somatic genome changes in prostate cancer. Using real-time methylation-specific PCR, we assessed the extent of hypermethylation at 16 CpG islands in DNA from seven prostate cancer cell lines (LNCaP, PC-3, DU-145, LAPC-4, CWR22Rv1, VCaP, and C42B), normal prostate epithelial cells, normal prostate stromal cells, 73 primary prostate cancers, 91 metastatic prostate cancers, and 25 noncancerous prostate tissues. We found that CpG islands at GSTP1, APC, RASSF1a, PTGS2, and MDR1 were hypermethylated in >85% of prostate cancers and cancer cell lines but not in normal prostate cells and tissues; CpG islands at EDNRB, ESR1, CDKN2a, and hMLH1 exhibited low to moderate rates of hypermethylation in prostate cancer tissues and cancer cell lines but were entirely unmethylated in normal tissues; and CpG islands at DAPK1, TIMP3, MGMT, CDKN2b,p14/ARF, and CDH1 were not abnormally hypermethylated in prostate cancers. Receiver operator characteristic curve analyses suggested that CpG island hypermethylation changes at GSTP1, APC, RASSF1a, PTGS2, and MDR1 in various combinations can distinguish primary prostate cancer from benign prostate tissues with sensitivities of 97.3-100% and specificities of 92-100%. Hypermethylation of the CpG island at EDNRB was correlated with the grade and stage of the primary prostate cancers. PTGS2 CpG island hypermethylation portended an increased risk of recurrence. Furthermore, CpG island hypermethylation patterns in prostate cancer metastases were very similar to the primary prostate cancers and tended to show greater differences between cases than between anatomical sites of metastasis.", 
"Background: Gene silencing by abnormal methylation of promoter regions of regulatory genes is commonly associated with cancer. Silenced tumor suppressor genes are obvious targets for reactivation by methylation inhibitors such as 5-azacytidine (5-Aza-CR) and 5-aza-2'-deoxycytidine (5-Aza-CdR). However, both compounds are chemically unstable and toxic and neither can be given orally. We characterized a new demethylating agent, zebularine [1-(beta-D-ribofuranosyl)-1,2-dihydropyrimidin-2-one], which is a chemically stable cytidine analog. Methods: We tested the ability of zebularine to reactivate a silenced Neurospora crassa gene using a hygromycin gene reactivation assay. We then analyzed the ability of zebularine to inhibit DNA methylation in C3H 10T1/2 C18 (10T1/2) mouse embryo cells as assayed by induction of a myogenic phenotype and in T24 human bladder carcinoma cells, using the methylation-sensitive single nucleotide primer extension (Ms-SNuPE) assay. We also evaluated the effects of zebularine (administered orally or intraperitoneally) on growth of EJ6 human bladder carcinoma cells grown in BALB/c nu/nu mice (five mice per group) and the in vivo reactivation of a methylated p16 gene in these cells. All statistical tests were two-sided. Results: In N. crassa, zebularine inhibited DNA methylation and reactivated a gene previously silenced by methylation. Zebularine induced the myogenic phenotype in 10T1/2 cells, which is a phenomenon unique to DNA methylation inhibitors. Zebularine reactivated a silenced p16 gene and demethylated its promoter region in T24 bladder carcinoma cells in vitro and in tumors grown in mice. Zebularine was only slightly cytotoxic to T24 cells in vitro (1 mM zebularine for 48 hours decreased plating efficiency by 17% [95% confidence interval (CI) = 12.8% to 21.2%]) and to tumor-bearing mice (average maximal weight change in mice treated with 1000 mg/kg zebularine = 11% [95% CI = 4% to 19%]). Compared with those in control mice, tumor volumes were statistically significantly reduced in mice treated with high-dose zebularine administered by intraperitoneal injection (P<.001) or by oral gavage (P<.001). Conclusions: Zebularine is a stable DNA demethylating agent and the first drug in its class able to reactivate an epigenetically silenced gene by oral administration.", 
"Human Forkhead-box (FOX) gene family consists of at least 43 members, including FOXA1, FOXA2, FOXA3, FOXB1, FOXC1, FOXC2, FOXD1, FOXD2, FOXD3, FOXD4, FOXD5 (FOXD4L1), FOXD6 (FOXD4L3), FOXE1, FOXE2, FOXE3, FOXF1, FOXF2, FOXG1 (FOXG1B), FOXH1, FOXI1, FOXJ1, FOXJ2, FOXJ3, FOXK1, FOXK2, FOXL1, FOXL2, FOXM1, FOXN1, FOXN2 (HTLF), FOXN3 (CHES1), FOXN4, FOXN5 (FOXR1), FOXN6 (FOXR2), FOXO1 (FOXO1A), FOXO2 (FOXO6), FOXO3 (FOXO3A), FOXO4 (MLLT7), FOXP1, FOXP2, FOXP3, FOXP4, and FOXQ1. FOXE3-FOXD2 (1p33), FOXQ1-FOXF2-FOXC1 (6p25.3), and FOXF1-FOXC2-FOXL1 (16q24.1) loci are FOX gene clusters within the human genome. Members of FOX subfamilies A-G, I-L and Q were grouped into class I FOX proteins, while members of FOX subfamilies H and M-P were grouped into class 2 FOX proteins. C-terminal basic region within the FOX domain was the common feature of class I FOX proteins. FOXH1 and FOXO1 mRNAs are expressed in human embryonic stem (ES) cells. FOXC1, FOXC2, FOXE1, FOXE3, FOXL2, FOXN1, FOXP2 and FOXP3 genes are mutated in human congenital disorders. FOXA1 gene is amplified and over-expressed in esophageal and lung cancer. FOXM1 gene is up-regulated in pancreatic cancer and basal cell carcinoma due to the transcriptional regulation by Sonic Hedgehog (SHH) pathway. FOXO1 gene is fused to PAX3 or PAX7 genes in rhabdomyosarcoma. FOXO3 and FOXO4 genes are fused to MLL gene in hematological malignancies. Deregulation of FOX family genes leads to congenital disorders, diabetes mellitus, or carcinogenesis. Expression profiles, genetic alterations and epigenetic changes of FOX family genes as well as binding proteins and target genes of FOX family transcription factors should be comprehensively investigated to develop novel therapeutics and preventives for human diseases.", 
" ", 
"A role for DNA demethylation in transcriptional regulation of genes expressed in differentiated somatic cells remains controversial. Here, we define a small region in the promoter-enhancer of the interleukin-2 (II2) gene that demethylates in T lymphocytes following activation, and remains demethylated thereafter. This epigenetic change was necessary and sufficient to enhance transcription in reporter plasmids. The demethylation process started as early as 20 minutes after stimulation and was not prevented by a G1 to S phase cell cycle inhibitor that blocks DNA replication. These results imply that this demethylation process proceeds by an active enzymatic mechanism.", 
"Recent studies from our laboratory suggest that gene-specific methylation changes in sputum could be good intermediate markers for the early detection of lung cancer and defining the efficacy of chemopreventive interventions. The purpose of our study was to determine the prevalence for aberrant promoter methylation of the p16, O-6-methylguanine-DNA methyltransferase (MGMT), death-associated protein (DAP) kinase, and Ras effector homologue (RASSFIA) genes in nonmalignant bronchial epithelial cells from current and former smokers in a hospital-based, case control study of lung cancer. The relationship between loss of heterozygosity, at 9p and p16 methylation in bronchial epithelium and the prevalence for methylation of these four genes in sputum from cancer-free, current and former smokers were also determined. Aberrant promoter methylation of p16 was seen in at least one bronchial epithelial site from 44% of cases and controls. Methylation of the DAP kinase gene was seen in only I site from 5 cases and 4 controls, whereas methylation of the RASSFIA was not detected in the bronchial epithelium. Promoter methylation for p16 and DAP kinase was seen as frequently in bronchial epithelium from current smokers as from former smokers. No promoter methylation of these genes was detected in bronchial epithelium from never-smokers. Methylation of the p16 gene was detected in sputum from 23 of 66 controls. DAP kinase gene promoter methylation was also seen in sputum from 16 controls, and 8 of these subjects were positive for p16 methylation. Methylation of the MGMT gene was seen in sputum from 9 controls, whereas RASSFIA promoter methylation was only seen in 2 controls. The correlation between p16 status in the bronchial epithelium obtained from lung lobes that did not contain the primary tumor and the tumor itself was examined. Seventeen of 18 tumors (94%) showed an absolute concordance, being either methylated in the tumor and at least I bronchial epithelial site, or unmethylated in both tumor and bronchial epithelium. These results indicate that aberrant promoter hypermethylation of the p16 gene, and to a lesser extent, DAP kinase, occurs frequently in the bronchial epithelium of lung cancer cases and cancer-free controls and persists after smoking cessation. The strong association seen between p16 methylation in the bronchial epithelium and corresponding primary tumor substantiates that inactivation of this gene,although not transforming by itself. is likely permissive for the acquisition of additional genetic and epigenetic changes leading to lung cancer.", 
"Cell-cell adhesion determines the polarity of cells and participates in the maintenance of the cell societies called tissues. Cell-cell adhesiveness is generally reduced in human cancers. Reduced intercellular adhesiveness allows cancer cells to disobey the social order, resulting in destruction of histological structure, which is the morphological hallmark of malignant tumors. Reduced intercellular adhesiveness is also indispensable for cancer invasion and metastasis. A tumor-suppressor gene product, E-cadherin, and its undercoat proteins, catenins, which connect cadherins to actin filaments, are located at lateral borders, concentrating on adherens junctions, of epithelial cells and establish firm cell-cell adhesion. The E-cadherin cell adhesion system in cancer cells is inactivated by various mechanisms that reflect the morphological and biological characteristics of the tumor. Silencing of the E-cadherin gene by DNA hypermethylation around the promoter region occurs frequently, even in precancerous conditions. In diffuse infiltrating cancers, mutations are found in the genes for E-cadherin and alpha- and beta-catenins. At the invading front of cancers, the E-cadherin cell adhesion system is inactivated by tyrosine phosphorylation of beta-catenin; an oncogene product, c-erbB-2 protein, is found to associate directly with beta-catenin. The E-cadherin cell adhesion system cross-talks with the Wingless/Wnt signaling pathway through beta-catenin, and expression of genes, which participate in cancer morphogenesis, may be regulated in conjunction with the Wingless/Wnt signaling pathway. Dysadherin, a newly identified cancer-associated cell membrane glycoprotein, down-regulates E-cadherin and promotes cancer metastasis. In conclusion, inactivation of the E-cadherin cell adhesion system by both genetic and epigenetic mechanisms plays a significant role during multistage human carcinogenesis.", 
"Background Hyperhomocysteinaemia occurs in several genetically determined and acquired disorders and is highly prevalent in patients with uraemia. In these disorders, homocysteine precursor S-adenosylhomocysteine, a powerful competitive inhibitor of S-adenosylmethionine-dependent methyltransferases, is increased, suggesting unbalanced methylation. We aimed to investigate whether DNA hypomethylation is present in patients with uraemia who also have hyperhomocysteinaemia and whether regulation of specific classes of genes, dependent on DNA methylation, is compromised. Methods We selected men with hyperhomocysteinaemia and uraemia who were having standard haemodialysis treatment, and compared them with healthy male controls. We measured the homocysteine concentration from plasma samples and obtained DNA and RNA samples from peripheral mononuclear cells. DNA methylation was assessed by cytosine extension assay and by Southern blotting. Allelic expression of pseudoautosomal and imprinted genes was investigated by analysis of suitable restriction fragment length polymorphisms. Findings Total DNA hypomethylation was higher in patients than in controls (z score -4.593, p=0.0006) and allelic expression was changed in both sex-linked and imprinted genes. The shift from monoallelic to biallelic expression was dependent on homocysteine concentrations. Folate therapy, a common method to reduce hyperhomocysteinaemia, restored DNA methylation to normal levels and corrected the patterns of gene expression. Interpretation Our results suggest that hyperhomocysteinaemia affects epigenetic control of gene expression, which can be reverted by folate treatment. Our data support the hypothesis that the toxic action of homocysteine can be mediated by macromolecule hypomethylation.", 
"DNA methylation is an epigenetic feature of DNA that influences cellular development and function, and aberrations of DNA methylation are a candidate mechanism for the development of cancer. Methylenetetrahydrofolate reductase (MTHFR) catalyzes the synthesis of 5-methyltetrahydrofolate, the methyl donor for methionine synthesis and the precursor of S-adenosylmethionine. S-adenosylmethionine is the universal methyl donor for methylation reactions, including that of DNA methylation. In the present study, we investigated whether a common C677T mutation in the MTHFR gene, which results in reduced enzyme activity in vitro, affects genomic DNA methylation. We selected 9 subjects homozygous for the wild-type MTHFR and 10 subjects homozygous for the mutation (T/T), Genomic DNA methylation was determined by an established enzymatic assay that measures the capacity of DNA to accept methyl groups in vitro, which is inversely related to endogenous methylation. DNA from subjects with the T/T MTHFR genotype had a significantly higher methyl group acceptance capacity (12,615 +/- 1836 dpm/2 mu g of DNA) compared with wild-type MTHFR (7843 1043 dpm/2 mu g of DNA; P < 0.05), indicating DNA hypomethylation in the T/T genotype, Furthermore, DNA methylation was directly and significantly related to RBC folate concentrations in persons with the T/T genotype, but not in those with wild-type MTHFR, These data are consistent with prior observations, which suggest that the T/T genotype is associated with impaired MTHFR activity in vivo and that the cellular impact of this impairment is determined, in part, by folate status. The relationship of genomic DNA hypomethylation in persons with the T/T MTHFR genotype to the development of cancer remains to be defined.", 
" ", 
"Methylation of cytosines within the CpG dinucleotide by DNA methyltransferases is involved in regulating transcription and chromatin structure, controlling the spread of parasitic elements, maintaining genome stability in the face of vast amounts of repetitive DNA, and X chromosome inactivation. Cellular DNA methylation is highly compartmentalized over the mammalian genome and this compartmentalization is essential for embryonic development. When the complicated mechanisms that control which DNA sequences become methylated go awry, a number of inherited genetic diseases and cancer may result. Much new information has recently come to light regarding how cellular DNA methylation patterns may be established during development and maintained in somatic cells. Emerging evidence indicates that various chromatin states such as histone modifications (acetylation and methylation) and nucleosome positioning (modulated by ATP-dependent chromatin remodeling machines) determine DNA methylation patterning. Additionally, various regulatory factors interacting with the DNA methyltransferases may direct them to specific DNA sequences, regulate their enzymatic activity, and allow their use as transcriptional repressors. Continued studies of the connections between DNA methylation and chromatin structure and the DNA methyltransferase-associated proteins, will likely reveal that many, if not all, epigenetic modifications of the genome are directly connected. Such studies should also yield new insights into treating diseases involving aberrant DNA methylation.", 
"Antigen and cytokine receptor signals act in synergy to direct the differentiation of CD4(+) T cells. These signals initiate reciprocal activation and silencing of the interferon-gamma (IFN-gamma) and interleukin 4 (IL-4) cytokine gene loci, changes that are heritably maintained in the resulting T helper type I (T(H)1) or T(H)2 cells and their progeny. Early, unpolarized transcription and chromatin remodeling of the poised cytokine genes of naive T cells is followed by consolidation and spreading of epigenetic changes and the establishment of self-reinforcing transcription factor networks. Recent studies have begun to elucidate the molecular mechanisms that establish and maintain polarized cytokine gene expression, and thus the cellular identity of differentiated helper T cells.", 
"We attempted to answer two central questions about epigenetic silencing of the tumor suppressor gene p16(INK4a) in this study: (1) whether the maintenance of associated histone modifications is dependent on DNA methylation and (2) whether such histone modifications can occur prior to DNA methylation. By coupling chromatin immunoprecipitation with gene targeting and the analysis of specific alleles, we found that elimination of DNA methylation from a p16(INK4a) allele resulted in profound changes in surrounding histones. After continued passage of such cells, methylation of histone H3 lysine-9 occurred in conjunction with re-silencing in the absence of DNA methylation. These results have important implications for understanding the biochemical events underlying the silencing of tumor suppressor genes and the resultant growth suppression.", 
"Genome-wide losses of DNA methylation have been regarded as a common epigenetic event in malignancies and may play crucial roles in carcinogenesis. Limited information is available on the global methylation status in normal tissues and other cancer types beyond colonic carcinoma. Here we applied the combined bisulfite restriction analysis PCR to evaluate the methylation status of LINE-1 repetitive sequences in genomic DNA derived from microdissected samples from several human normal and neoplastic tissues. We found that methylation of LINE-1 in leukocytes was independent of age and gender. In contrast, normal tissues from different organs showed tissue-specific levels of methylated LINE-1. Globally, most carcinomas including breast, colon, lung, head and neck, bladder, esophagus, liver, prostate, and stomach, revealed a greater percentage of hypomethylation than their normal tissue counterparts. Furthermore, DNA derived from sera of patients with carcinoma displayed more LINE-1 hypomethylation than those of noncarcinoma individuals. Finally, in a colonic carcinogenesis model, we detected significantly greater hypomethylation in carcinoma than those of dysplastic polyp and histological normal colonic epithelium. Thus, the methylation status is a unique feature of a specific tissue type and the global hypomethylation is a common epigenetic process in cancer, which may progressively evolve during multistage carcinogenesis.", 
"Cancer is a process driven by the accumulation of abnormalities in gene function. While many of these changes are genetic, epigenetically mediated changes in gene expression are being increasingly appreciated. This latter process emphasizes the need to understand two key components of heritable, but reversible, modulation of gene promoter function that are closely tied to one another - formation of chromatin which modulates transcription and establishing patterns of DNA methylation, The link lies first in the recruitment to methylated cytosines of a family of methyl-CpG binding domain proteins (MBDs), which are direct transcriptional repressors and can complex with transcriptional core-pressors including histone deacetylases (HDACs), Additionally, the proteins that catalyze DNA methylation, DNA methyltransferases (DNMTs), also directly repress transcription and associate with HDACs. Regulation of these above chromatin-DNA methylation interactions as a function of DNA replication timing is emerging as a key event in the inheritance of transcriptionally repressed domains of the genome. Importantly, synergy between HDAC activity and DNA methylation is operative for a key epigenetic abnormality in cancer cells, transcriptional silencing of tumor suppressor genes. This change has now been recognized for genes that are essential for normal regulation of virtually every major cell function including cell growth, differentiation, apoptosis, DNA repair, and cell-cell, cell-substratum interaction. Understanding the molecular determinants of both normal and abnormal patterns of chromatin formation and DNA methylation thus holds great promise for our understanding of cancer and for means to better diagnose, prevent, and treat this means to better disease.", 
"Post-translational modification of the histories of chromatin has a fundamental role in regulating gene expression. Enzymes involved in these epigenetic events include histone deacetylases (class I and class II), which can be inhibited by a structurally diverse group of small molecules. These histone deacetylase inhibitors induce growth arrest, differentiation and/or apoptosis of cancer cells in vitro and in vivo. Results of clinical trials with several of these agents have indicated that they are well tolerated at doses that have anti-tumour activity.", 
"The concept of stem-cell plasticity received strong support from a recent observation that extensively passaged, clonally derived neural stem cells could contribute to hematopoiesis. We investigated whether hematopoietic potential was a consistent or unusual feature of neural stem cells, and whether it depended on the extent of in vitro passaging before transplantation. Here we transplanted over 128 x 10(6) neurosphere cells into 128 host animals; however, we never observed contribution to hematopoiesis, irrespective of the number of passages and despite the use of an assay that could detect the contribution of a single blood stem cell to hematopoietic repopulation. Although extensively cultured neurosphere cells continued to generate neural progeny, marked changes in their growth properties occurred, including changes in growth-factor dependence, cell-cycle kinetics, cell adhesion and gene expression. Our results exclude hematopoietic competence as a consistent property of intravenously infused neural stem cells. However, the consistent changes that occurred during extended passaging are compatible with genetic or epigenetic alterations and suggest that rare transformation events may account for the neural-to-blood fate switch originally reported.", 
"Epigenetic modifications of cytosine residues in DNA and the amino termini of histone proteins have emerged as key mechanisms in chromatin remodeling, impacting both the transcriptional regulation and the establishment of chromosomal domains. Using the chromatin immunoprecipitation (ChIP) assay, we demonstrate that aberrantly silenced genes in cancer cells exhibit a heterochromatic structure that is characterized by histone H3 lysine 9 (H3-K9) hypermethylation and histone H3 lysine 4 (H3-K4) hypomethylation. This aberrant heterochromatin is incompatible with transcriptional initiation but does not inhibit elongation by RNA polymerase II. H3-K9 methylation may, therefore, play a role in the silencing of tumor-suppressor genes in cancer. Treatment with 5-aza-2'-deoxycytidine (5-Aza-CdR), previously known for its ability to inhibit cytosine methylation, induced a rapid and substantial remodeling of the heterochromatic domains of the p14ARF/p16INK4a locus in T24 bladder cancer cells, reducing levels of dimethylated H3-K9 and increasing levels of dimethylated H3-K4 at this locus. In addition, 5-Aza-CdR increased acetylation and H3-K4 methylation at the unmethylated p14 promoter, suggesting it can induce chromatin remodeling independently of its effects on cytosine methylation.", 
"E-cadherin is a cell-cell adhesion protein fulfilling a prominent role in epithelial differentiation. Data from model systems suggest that E-cadherin is a potent invasion/tumor suppressor of breast cancer. Consistent with this role in breast cancer progression, partial or complete loss of E-cadherin expression has been found to correlate with poor prognosis in breast cancer patients. The E-cadherin gene (CDH1) is located on human chromosome 16q22.1, a region frequently affected with loss of heterozygosity in sporadic breast cancer. Invasive lobular breast carcinomas, which are typically completely E-cadherin-negative, often show inactivating mutations in combination with loss of heterozygosity of the wild-type CDH1 allele. Mutations were found at early noninvasive stages, thus associating E-cadherin mutations with loss of cell growth control and defining CDH1 as the tumor suppressor for the lobular breast cancer subtype. Ductal breast cancers in general show heterogeneous loss of E-cadherin expression, associated with epigenetic transcriptional downregulation. It is proposed that the microenvironment at the invasive front is transiently downregulating E-cadherin transcription. This can be associated with induction of nonepithelial cadherins.", 
"Epigenetic alterations in human cancers include global DNA hypomethylation, gene hypomethylation and promoter hypermethylation, and loss of imprinting (LOI) of the insulin-like growth factor-II gene (IGF2). A mechanism for LOI described previously is hypermethylation of a differentially methylated region (DMR) upstream of the H19 gene, allowing activation of the normally silent maternal allele of IGF2. Here we show that this mechanism does not apply to colorectal cancers, which show hypomethylation of the H19 DMR as well as a DMR upstream of exon 3 of IGF2. This hypomethylation is found in both colorectal cancers and normal mucosa from the same patients, and in cell lines with somatic cell knockout of DNA methyltransferases DNMT1 and DNMT3B. These data suggest that hypomethylation is a mechanism for LOI, that the popular IGF2-H19 enhancer competition model for IGF2 imprinting does not apply to the human colon, and that an alternative model for LOI would involve a transcriptional repressor acting on the normally silent maternal allele of IGF2.", 
"DNA methylation is an important epigenetic mechanism of transcriptional control. DNA methylation plays an essential role in maintaining cellular function, and changes in methylation patterns may contribute to the development of cancer. Aberrant methylation of DNA (global hypomethylation accompanied by region-specific hypermethylation) is frequently found in tumor cells. Global hypomethylation can result in chromosome instability, and hypermethylation has been associated with the inaction of tumor suppressor genes. Preclinical and clinical studies suggest that part of the cancer-protective effects associated with several bioactive food components may relate to DNA methylation patterns. Dietary factors that are involved in one-carbon metabolism provide the most compelling data for the interaction of nutrients and DNA methylation because they influence the supply of methyl groups, and therefore the biochemical pathways of methylation processes. These nutrients include folate, vitamin B-12, vitamin B-6, methionine, and choline. However, looking at individual nutrients may be too simplistic. Dietary methyl (folate, choline, and methionine) deficiency in combination causes decreased tissue S-adenosylmethionine, global DNA hypomethylation, hepatic steatosis, cirrhosis, and ultimately hepatic tumorigenesis in rodents in the absence of carcinogen treatment. Other dietary components such as vitamin B-12, alcohol, and selenium may modify the response to inadequate dietary folate.", 
"Cadmium is a human carcinogen that likely acts via epigenetic mechanisms. Since DNA methylation alterations represent an important epigenetic event linked to cancer, the effect of cadmium on DNA methyltransferase (MeTase) activity was examined using in vitro (TRL1215 rat liver cells) and ex vivo (M.SssI DNA MeTase) systems. Cadmium effectively inhibited DNA MeTases in a manner that was noncompetitive with respect to substrate (DNA), indicating an interaction with the DNA binding domain rather than the active site. Based on these results, the effects of prolonged cadmium exposure on DNA MeTase and genomic DNA methylation in TRL1215 cells were studied. After I week of exposure to 0-2.5 muM cadmium, DNA MeTase activity was reduced (up to 40%) in a concentration-dependent fashion, while genomic DNA methylation showed slight but significant reductions at the two highest concentrations. After 10 weeks of exposure, the cells exhibited indications of transformation, including hyperproliferation, increased invasiveness, and decreased serum dependence. Unexpectedly, these cadmium-transformed cells exhibited significant increases in DNA methylation and DNA MeTase activity. These results indicate that, while cadmium is an effective inhibitor of DNA MeTase and initially induces DNA hypomethylation, prolonged exposure results in DNA hypermethylation and enhanced DNA MeTase activity. (C) 2003 Elsevier Science (USA). All rights reserved.", 
"The microenvironment of solid tumours contains regions of poor oxygenation and high acidity. Growing evidence from clinical and experimental studies points to a fundamental role for hypoxia in metastatic progression. Prolonged hypoxia increases genomic instability, genomic heterogeneity, and may act as a selective pressure for tumour cell variants. Hypoxia can also act in an epigenetic fashion, altering the expression of genes. Hypoxia-induced changes in gene expression alter non-specific stress responses, anaerobic metabolism, angiogenesis, tissue remodeling, and cell-cell contacts. Experimental studies have demonstrated that inhibition of proteins involved in these processes can modify metastasis formation, suggesting a causal role in metastatic progression. Recent advances in high-throughput screening techniques have allowed identification of many hypoxia-induced genes that are involved in the processes associated with metastasis. Here we review the epigenetic control of gene expression by the hypoxic microenvironment and its potential contribution to metastatic progression.", 
"The neoplastic process may involve a cancer stem cell. This concept has emerged largely from the careful analysis of tumour biopsy systems from haematological, breast and brain tumours. However, the experimental systems necessary to provide the cellular and molecular evidence to support this important concept have been lacking. We have used adult mesenchymal stem cells (hMSC) transduced with the telomerase hTERT gene to investigate the neoplastic potential of adult stem cells. The hTERT-transduced line, hMSC-TERT20 at population doubling level (PDL) 256 showed loss of contact inhibition, anchorage independence and formed tumours in 10/10 mice. hMSC-TERT4 showed loss of contact inhibition at PDL 95, but did not exhibit anchorage independence and did not form tumours in mice. Both lines had a normal karyotype but showed deletion of the Ink4a/ARF locus. At later passage, hMSC-TERT4 also acquired an activating mutation in KRAS. In hMSC-TERT20, expression of the cell cycle-associated gene, DBCCR1 was lost due to promoter hypermethylation. This epigenetic event correlated with acquisition of tumorigenicity. These data suggest that the adult hMSCs can be targets for neoplastic transformation and have implications for the development of novel anticancer therapeutics and for the use of hMSC in tissue engineering and transplantation protocols.", 
"The DNA repair protein O-6-methylguanine DNA methyltransferase (MGMT) removes alkyl adducts from the O-6 position of guanine, MGMT expression is decreased in some tumor tissues, and lack of activity has been observed in some cell lines. Loss of expression is rarely due to deletion, mutation, or rearrangement of the MGMT gene, but methylation of discrete regions of the CpG island of MGMT has been associated with the silencing of the gene in cell lines. We used methylation-specific PCR to study the promoter methylation of the MGMT gene. All normal tissues and expressing dancer cell lines were unmethylated, whereas nonexpressing cancer cell lines were methylated. Among the more than 500 primary human tumors examined, MGMT hypermethylation was present in a subset of specific types of cancer. In gliomas and colorectal carcinomas, aberrant methylation was detected in 40% of the tumors, whereas in non-small cell lung carcinomas, lymphomas, and head and neck carcinomas, this alteration was found in 25% of the tumors. MGMT methylation was found rarely or not at all in other tumor types. We also analyzed MGMT expression by immunohistochemistry in relation to the methylation status in 31 primary tumors. The presence of aberrant hypermethylation was associated with loss of MGMT protein, in contrast to retention of protein in the majority of tumors without aberrant hypermethylation, Our results suggest that epigenetic inactivation of MGMT plays an important role in primary human neoplasia.", 
"Helper T (Th) cell differentiation is highly regulated by cytokines but initiated by mitogens. By examining gene expression in discrete generations of dividing cells, we have delineated the relationship between proliferation and differentiation. Initial expression of IL-2 is cell cycle-independent, whereas effector cytokine expression is cell cycle-dependent. IFN gamma expression increases in frequency with successive cell cycles, while IL-4 expression requires three cell divisions. Cell cycle progression and cytokine signaling act in concert Po relieve epigenetic repression and can be supplanted by agents that hyperacetylate histones and demethylate DNA. Terminally differentiated cells exhibit stable epigenetic modification and cell cycle-independent gene expression. These data reveal a novel mechanism governing Th cell fate that initially integrates proliferative and differentiative signals and subsequently maintains stability of the differentiated state.", 
"Endoglin (CD105), an accessory protein of the TGF-beta receptor superfamily, is highly expressed on endothelial cells. Hereditary hemorrhagic telangiectasia type 1 (HHT1) is associated with mutations in the Endoglin gene, leading to haploinsufficiency. To generate a disease model and ascertain the role of endoglin in development, we generated mice lacking 1 or both copies of the gene. Endoglin null embryos die at gestational day 10.0-10.5 due to defects in vessel and heart development. Vessel formation appears normal until hemorrhage occurs in yolk sacs and embryos. The primitive vascular plexus of the yolk sac fails to mature into defined vessels, and vascular channels dilate and rupture. Internal bleeding is seen in the peritoneal cavity, implying fragile vessels. Heart development is arrested at day 9.0, and the atrioventricular canal endocardium fails to undergo mesenchymal transformation and cushion-tissue formation. These data suggest that endoglin is critical for both angiogenesis and heart valve formation. Some heterozygotes, either with an inbred 123/Ola or mixed C57BL/6-129/Ola background, show signs of HHT, such as telangiectases or recurrent nosebleeds. In this murine model of HHT, it appears that epigenetic factors and modifier genes, some of which are present in 129/Ola, contribute to disease heterogeneity.", 
"L-Glutamic acid is a major excitatory neurotransmitter in the mammalian central nervous system. The termination of the glutamatergic transmission and the clearance of the excessive, neurotoxic concentrations of glutamate is ensured by a high affinity glutamate uptake system. Four homologous types of Na/K-dependent high affinity glutamate transporters, glutamate/aspartate transporter, glutamate transporter 1, excitatory amino acid carrier 1, and excitatory amino acid transporter 4, have recently been cloned and were assigned to a separate gene family, together with two neutral amino acid carriers, alanine/serine/cysteine transporter 1/serine/alanine/threonine transporter and adipocyte amino acid transporter. The genomic organization of these transporters is still under investigation. Very little is known about the nature of the factors and molecular mechanisms that regulate developmental, regional, and cell type-specific expression of the glutamate transporters and their aberrant functioning in neurodegenerative diseases (e.g., amyotrophic lateral sclerosis and Alzheimer's disease). Some experimental conditions (e.g., ischemia, corticostriatal lesions, hyperosmolarity, culturing conditions) and several naturally occurring and synthetic compounds (e.g., glutamate receptor agonists, dopamine, alpha(1)- and beta-adrenergic agonists, cAMP, phorbol esters, arachidonic acid, nitric oxide, oxygen free radicals, amyloid beta-peptide, tumor necrosis factor-alpha, glucocorticosteroids, unidentified neuronal factors) affect the molecular expression and activity of glutamate transporters. Further elucidation of the molecular events that link epigenetic signals with transcriptional and post-transcriptional mechanisms (e.g., alternative splicing, translation and post-translational modifications) is crucial for the development of selective pharmacological tools and strategies interfering with the expression of the individual glutamate transporters.", 
"Mutation of DNA mismatch repair genes has rarely been documented in sporadic gastric carcinoma with microsatellite instability (MSI), In sporadic colorectal carcinoma, hMLH1 promoter methylation associated with protein loss is found in the majority of high-frequency MSI cases. We investigated a series of 35 sporadic gastric carcinomas stratified into high-frequency MSI (MSI-H), low-frequency MSI (MSI-L) and microsatellite stable (MSS) groups and found that hypermethylation of the CPG island in the hMLH1 promoter region was present in 100% of MSI-H sporadic gastric carcinomas. In 90% of cases, there was an associated complete loss of hMLH1 protein, as detected by immunohistochemistry, and a markedly lowered hMLH1 mRNA level. This loss of hMLH1 protein occurred in the MSI-H invasive tumor but not in the adjacent carcinoma-irt situ or dysplastic components that were MSS. The MSI-L and MSS forms of gastric carcinoma all showed predominantly unmethylated hll;hMLH1 promoter, positive hMLH1 protein and high hMLH1 mRNA level. On the other hand, hMSH2 protein was expressed in all of the tumors irrespective of the MSI status. Our results suggest that high-frequency MSI in sporadic gastric cancer is mostly due to epigenetic inactivation of hMLH1 in association with promoter methylation, and the loss of hMLH1 protein is a significant event in the development of invasive tumor.", 
"Human gastric carcinoma shows a higher prevalence of microsatellite instability (MSI) than does any other type of sporadic human cancer. The reasons for this high Frequency of MSI are not get known. In contrast to endometrial and colorectal carcinoma, mutations of the DNA mismatch repair (MMR) genes hMLH1 or hMSH2 have not been described in gastric carcinoma. However, hypermethylation of the hMLH1 MMR gene promoter is quite common in MSI-positive endometrial and colorectal cancers. This hypermethylation has been associated with hMLH1 transcriptional blockade, which is reversible with demethylation, suggesting that an epigenetic mechanism underlies hMLH1 gene inactivation and MMR deficiency. Therefore, we studied the prevalence of hMLH1 promoter hypermethylation in a total of 65 gastric tumors: 18 with frequent MSI (MSI-H), 8 with infrequent MSI(MSI-L), and 39 that were MSI negative. We found a striking association between hMLH1 promoter hypermethylation and MSI: of 18 MSI-H tumors, 14 (77.8%) showed hg permethylation, whereas 6 of 8 MSI-L tumors (75%) were hypermethylated at hMLH1. In contrast, only; 1 of 39 (2.6%) MSI-negative tumors demonstrated hMLH1 hypermethylation (P < 0.0001 for MSI-H or MSI-L, versus MSI-negative). Moreover, hypermethylated cancers demonstrated diminished expression of hMLH1 protein by both immunohistochemistry and Western blotting, whereas nonhypermethylated tumors expressed abundant hMLH1 protein. These data indicate that hypermethylation of hMLH1 is strongly associated with MSI in gastric cancers and suggest an epigenetic mechanism by which defective MMR occurs in this group of cancers.", 
"Mutations of the BRCA1 gene in tumor DNA from patients with sporadic breast cancer have not yet been observed. Nevertheless, BRCA1 activity is markedly decreased in invasive breast tumors, Previous reports have shown that hypermethylation of the promoter region is an alternative mechanism to mutation for the inactivation of tumor suppressor genes. We examined the BRCA1 promoter region for hypermethylation by Southern blotting, Hypermethylation was observed in two of seven sporadic breast carcinomas but not in any normal tissues, The hypermethylation was not an artifact because a control region was unmethylated in the two tumors. Although not all tumors were hypermethylated, these observations are consistent with an important role for epigenetic mechanisms in human cancer.", 
"The p73 gene is located on 1p36.2-3, a region that is frequently deleted in human cancer. Because p73 encodes for a protein that is both structurally and functionally homologous to the p53 protein, p73 has been postulated to be a candidate tumor suppressor gene. To date, however, mutations of p73 have not been found. To study methylation of the p73 5'CpG island, a human bacterial artificial chromosome clone containing exon 1 and the 5' region of p73 was isolated. There was no evidence for p73 exon 1 methylation in normal tissues. In contrast, p73 was aberrantly methylated in approximately 30% of primary acute lymphoblastic leukemias (ALLs) and Burkitt's lymphomas. There was no evidence for methylation in any other types of hematological malignancies or solid tumors examined. In both leukemia cell lines and primary ALLs, methylation was associated with transcriptional loss of p73 by reverse transcription-PCR, mie used single-strand conformational polymorphisms to screen fur paint mutations in a series of primary ALLs and found no mutations leading to a change in protein structure. Our results show that methylation of p73 is a frequent event in specific types of hematological malignancies and suggest that epigenetic silencing of p73 could have important consequences for cell-cycle regulation.", 
" ", 
"Loss of imprinting (LOI) is an epigenetic alteration of some cancers involving loss of parental origin-specific expression of imprinted genes. We observed LOI of the insulin-like growth factor-ii gene in twelve of twenty-seven informative colorectal cancer patients (44%), as well as in the matched normal colonic mucosa of the patients with LOI in their cancers, and in peripheral blood samples of four patients. Ten of eleven cancers (91%) with microsatellite instability showed LOI, compared with only two of sixteen tumors (12%) without microsatellite instability (P< 0.001). Control patients without cancer showed LOI in colonic mucosa of only two of sixteen cases (12%, P < 0.001) and two of fifteen blood samples (13%, P < 0.001). These data suggest that LOI in tumor and normal tissue identifies most colorectal cancer patients with microsatellite instability in their tumors, and that LOI may identify an important subset of the population with cancer or at risk of developing cancer.", 
"Purpose: Patients treated with identical radiotherapy schedules show a substantial variation in the degree of acute and late normal tissue reactions. To identify any possible contributing factors to this phenomenon, we have analyzed the treatments of 402 breast cancer patients. Methods and Materials: The patients received adjuvant postoperative radiotherapy between 1972 and 1985 and have been followed up since then. Multivariate analyses were performed with peak reflectance erythema and peak acute reaction score as endpoints for the acute reactions, and with progression rate of telangiectasia as well as telangiectasia score as endpoints for the late reactions. Twenty patient- and treatment-related factors were tested such as age, menopausal status, hemoglobin level, serum calcium, smoking habits, hypothyroidism, diabetes, hypertension, blood pressure, cardiovascular and autoimmune disease, the influence of hormone therapy and chemotherapy, pretreatment reflectance value, acute skin reactions, radiation quality, individual dose, bilateral fields, and the total effect (TE) for the dose schedule applied. Results: The TE was a strong prognostic factor for all endpoints. In addition to TE, blood pressure was prognostic for the peak erythema measured by reflectance spectrophotometry, and the pretreatment reflectance value was prognostic for the acute score. The only independent prognostic factors found for the progression of skin telangiectasia and telangiectasia score except for TE were the individual dose and the acute skin reactions. Conclusions: These factors explained at most about 30% of the variance describing the total patient-to-patient variability for each endpoint. The remaining variability is still unexplained but may be related to individual differences in cellular radiosensitivity, partly determined by genetic variations and partly by unknown epigenetic factors. Copyright (C) 1996 Elsevier Science Inc.", 
"The early epidemiological data indicated different carcinogenic risks from inhalation of different nickel compounds, but it was not clear what characteristics governed the intrinsic carcinogenic hazard of the various nickel compounds. Based on the earlier results, all soluble and insoluble nickel compounds were assumed to have the same carcinogenic mechanism albeit different potencies, Recent in vivo and in vitro studies challenged this assumption. In this paper an attempt is made to integrate the most relevant human, animal, and in vitro data into a general model that can help understand the different carcinogenic potentials of the various nickel compounds. In this perspective, it is recognized that there are two main components that could contribute to the development of lung cancer via exposure to certain nickel compounds, The first component corresponds to the heritable changes (genetic or epigenetic) derived from the direct or indirect actions of nickel compounds, The second component may be the promotion of cell proliferation elicited by certain nickel compounds. The different contributions of three nickel compounds to these two components are presented. This paper emphasizes the importance of recognizing the individuality of the different nickel species in reaching regulatory decisions and the fact that different risk assessment considerations may apply for compounds that appear to produce immortality and cancer by genetic/epigenetic mechanisms (like nickel subsulfide), compounds that may present a threshold for the induction of tumors in rats (like high-temperature nickel oxide), or compounds that may only have an enhancing effect on carcinogenicity (like nickel sulfate). (C) 1997 Academic Press.", 
"Chronic exposure to high doses of phenobarbital (PB) causes hepatocellular adenomas in both mice and rats and hepatocellular carcinomas in some strains of mice, Long term PB therapy has not been found to cause human tumors, PB is not DNA reactive, and most genotoxicity tests have yielded negative results, PB has been extensively studied as an epigenetic, rodent liver tumor promoter, At exposures causing rodent liver tumors, PB has measurable effects on hepatocytes: PB inhibits cell-to-cell communication; PB induces enzymes, including P450 cytochromes; PB stimulates proliferation and inhibits apoptosis of hepatocytes in neoplastic foci, Threshold exposures for some of these endpoints coincide with the threshold exposure for tumorigenesis.", 
"T helper (Th) lymphocytes, when reactivated, recall expression of those cytokines they had been instructed to express in earlier activations, even in the absence of specific cytokine-inducing factors. In cells that memorize their expression, the cytokine genes are modified by chromatin rearrangement and demethylation, suggesting that they have been somatically imprinted. Here we show, by using inhibitors blocking the cell cycle in various stages, that for the instruction of a Th cell to express interleukin (IL)-4 or IL-10 upon restimulation, entry of the cell into the S phase of the first cell cycle after initial activation is required. Separation of the IL-4 receptor (IL-4R) and T cell antigen receptor (TCR) signals in time, demonstrates that this instruction is dependent on concomitant signaling from both receptors. In Th cells, inhibited to progress into the first S phase after activation, the IL-4R and TCR signals can be memorized for at least 1 d, priming the T cell, to become instructed for expression of IL-4 upon restimulation, when entering the S phase after release of the cell cycle block. The requirement of the initial S phase of T cell activation, for instruction of Th cells to express IL-4 or IL-10 upon restimulation points to the decisive role of epigenetic modification of cytokine genes as a molecular correlate of the memory to express particular cytokines.", 
"We have developed a quantitative method for methylation analysis of the p16 gene based on real-time methylation-specific PCR (MSP). Realtime MSP is sensitive enough to detect down to 10 genome equivalents of the methylated p16 sequence. Application of real-time MSP to DNA from tumor-derived cell Lines revealed complete concordance with conventional MSP analysis. Quantitative data generated by real-time MSP were expressed as the methylation index, which was defined as the percentage of bisulfite-converted DNA that consisted of methylated target sequences. The methylation index was shown to be inversely correlated with p16 gene transcription during demethylation treatment of cell lines with 5-aza-2'-deoxycytidine. The application of real-time MSP to bone marrow aspirates from patients with multiple myeloma revealed complete concordance with conventional MSP analysis. Real-time quantitative MSP may have applications in elucidating diverse biological processes involving DNA methylation and mag become a valuable diagnostic tool for detecting tumor-associated epigenetic changes in cancer patients.", 
"Hypermethylation of tumor suppressor genes and other genes functionally important in the neoplastic process is a recently recognized process. This epigenetic process is characterized by loss of function of these genes associated with transcriptional loss in the absence of structural alterations. The growing list of genes inactivated by promoter region hypermethylation provide an opportunity to examine the patterns of inactivation of such genes and provide clues as to the roles these events play in the neoplastic process.", 
"To determine whether neuroblastomas acquire a sustained drug-resistant phenotype from exposure to chemotherapeutic agents given to patients in vivo, we studied neuroblastoma cell lines established at different points of therapy: six at diagnosis before therapy (DX), six at progressive disease during induction therapy (PD-Ind), and five at relapse after intensive chemoradiotherapy and bone marrow transplantation (PD-BMT). Cells were maintained in the absence of drug selective pressure. Dose-response curves of melphalan, cisplatin, carboplatin, doxorubicin, and etoposide for the cell line panel were determined by measuring cytotoxicity with a 96-well-plate digital imaging microscopy (DIMSCAN) microassay. Drug resistance of cell lines progressively increased with the intensity of therapy delivered in vivo. The greatest resistance was seen in PD-BMT cell lines: IC90 values in PD-BMT cell lines were higher than clinically achievable drug levels by 1-37 times for melphalan, 1-9 times for carboplatin, 25-78 times for cisplatin, 6-719 times for doxorubicin, and 3-52 times for etoposide. Genomic amplification of MYCN did not correlate with resistance. Cross-resistance by Pearson correlation (r greater than or equal to 0.6) was observed between: (a) cisplatin + doxorubicin; (b) carboplatin + cisplatin, etoposide, or melphalan; (c) etoposide + cisplatin, melphalan, or doxorubicin. These data indicate that during therapy, neuroblastomas can acquire resistance to cytotoxic drugs because of the population expansion of tumor cells possessing stable genetic or epigenetic alterations that confer resistance.", 
"The mouse skin model of chemical carcinogenesis has been very well characterized with respect to epigenetic changes, which occur during tumour cell initiation, promotion and progression. The use of transgenic and gene knock-out mice has contributed greatly to knowledge in this area. The H-ras genetic locus has been shown to undergo multiple genetic changes, including mutagenic activation, amplification of the mutant gene, and loss of the normal allele, These different genetic events lead to thresholds of ras activity which contribute to different stages along the pathway to neoplasia. The genetic and epigenetic events which lead to tumour invasion and metastasis hale been less well characterized than studies on tumour initiation and promotion, despite the fact that it is metastases which ultimately kill the animal/patient. In the mouse skin model, loss of p53 contributes to malignant conversion. Gene deletion of the INK4 locus is associated with transformation to a highly invasive spindle cell tumor phenotype, This spindle cell transformation can also be induced in vitro or in vivo by TGF beta 1, possible by synergizing with mutant H-ras. TGF beta can have both positive and negative effects on tumourigenesis, acting early as a tumour suppresser, but later as a stimulator of tumour invasion. It is this latter effect which may be clinically more significant, since many human tumours overexpress TGF beta, yet the majority still retain the intracellular signaling systems necessary for the cell to respond to this growth factor. Copyright (C) 1999 John Wiley & Sons, Ltd.", 
"Aberrant 5' CpG island methylation is an alternative mechanism of gene inactivation during the development of cancer as demonstrated for several tumor-suppressor genes. Also, marked relationship of microsatellite instability (MSI) and DNA methylation has been reported in sporadic colorectal cancer, which is a result of epigenetic inactivation of hMLHI in association of promoter hypermethylation, In the present study, we investigated the 5' CpG island hypermethylation of hMLHI, E-cadherin and p16 in 61 primary gastric cancers (GCs) by using combined bisulfite restriction analysis (COBRA) and methylation-specific FCR (MSP), and their MSI status. Of 61 GCs investigated, 5 (8.1%) tumors presented hMLHI methylation, 16 (26.2%) and 25 (40.9%) showed E-cadherin and p16 methylation respectively, and 8 (13.1%) presented high-frequency MSI (MSI-H). Of the a MSI-H patients, 5 presented hMLHI methylation, whereas no low-frequency MSI (MSI-L) and microsatellite stable (MSS) cases exhibited hMLHI methylation (5/8 vs. 0/43, p<0.00001). Furthermore, these patients also presented E-cadherin and p16 hypermethylation. Our data showed a significant correlation between hMLHI methylation and MSI in GC, and suggested that a common mechanism of aberrant de novo methylation can be postulated in these cancers. (C) 1999 Wiley-Liss, Inc.", 
"The cyclin-dependent kinase inhibitor p16 (p16(INK4A)/CDKN2/MTS1) is a potent inhibitor of the cyclin D-dependent phosphorylation of the retinoblastoma gene (Rb) product, the inactivation of which induces loss of Rb-dependent G1 arrest through inappropriate phosphorylation of the Rb protein. To analyse the role of po16(INK4A) as a tumor suppressor in the genesis of non small cell lung cancers (NSCLC) and correlate loss of p16(INK4A) protein expression to genetic or epigenetic mechanisms, we have performed a comprehensive study of p16 status in a series of 43 NSCLC. To this end, we have investigated p16(INK4A) protein expression with immunohistochemistry, deletions of the gene by FISH, and determined the methylation status of exon 1 alpha using a PCR-based methylation assay. Finally, possible mutations were studied by SSCP and subsequent sequencing, Twenty one of the 43 (49%) NSCLC studied exhibited an absence of p16(INK4A) nuclear staining. Of these, three (14%) had frameshift or missense mutations, seven (33%) displayed methylation of exon1 alpha and 10 (48%) displayed homozygous deletions, In total, 95% of the tumors with p16(INK4A) negative staining carried one of these three alternative genetic or epigenetic alterations. Furthermore, a high degree of chromosome 9 polysomy was found (58%) in those tumors with p16(INK4A) inactivation. Taken together these results suggest that deregulation of the p16 gene locus is a frequently occurring event in NSCLC through distinct mechanisms including rare point mutations, promotor methylation and frequent homozygous deletions. Furthermore, our data show that immunohistochemistry is a rapid and an accurate technique for screening of p16(INK4A) gene inactivation events that result in loss of protein expression.", 
"Inactivation of p16(INK4) tumor suppressor gene function is frequently observed in breast cancer. We examined p16(INK4) expression in human mammary epithelial cell (HMEC) cultures established from four normal donors. Normal HMECs divide a limited number of times before proliferation ceases in a state referred to as selection (or M-o). The cell subpopulation that emerges spontaneously from selection undergoes a further limited period of proliferation before senescence. By immunofluorescence and Western blot analysis of four independent cultures, me have shown Loss of p16(INK4) expression in postselection HMECs. In contrast, p16(INK4) was present in both early and late passage fibroblasts from the same individuals. Bisulfite genomic sequencing revealed extensive methylation of the p16(INK4) CPG island in post- but not preselection cells. Thus, the extended period of growth observed in postselection HMECs is associated with hypermethylation of the p16(INK4) CpG island and Loss of p16(INK4) expression. Although postselection HMECs are widely considered to be normal, these data indicate that they have sustained an epigenetic alteration.", 
"Chromatin ir the natural substrate for the control of gene expression. Chromatin contains DNA, the transcriptional machinery and structural proteins such as histones. Recent advances demonstrate that transcriotional activity of a gene Is Inr largely controlled by the packaging of the template within chromatin. The covalent modification of chromatin provides an attractive mechanism for establishing and maintaining stable states of gene activity. DNA methylation and histone acetylation alter the nucleosomal infrastructure to repress or activate transcription. These covalent modifications have causal roles in both promoter-specific events and the global control of chromosomal activity. DNA methylation and histone acetylation have a major impact in both oncogenic transformation and normal development.", 
"Transforming Growth Factor-beta (TGF beta) is the most potent known inhibitor of the progression of normal mammary epithelial cells through the cell cycle. During the early stages of breast cancer development, the transformed epithelial cells appear to still be sensitive to TGF beta-mediated growth arrest, and TGF beta can act as an anti-tumor promoter. In contrast, advanced breast cancers are mostly refractory to TGF beta-mediated growth inhibition and produce large amounts of TGF beta, which may enhance tumor cell invasion and metastasis by its effects on extracellular matrix. We postulate that this seemingly paradoxical switch in the responsiveness of tumor cells to TGF beta during progression is the consequence of the activation of the latent TGF beta that is produced and deposited into the tumor microenvironment, thereby driving the clonal expansion of TGF beta-resistant tumor cells. While tumor cells themselves may activate TGF beta, recent observations suggest that environmental tumor promoters or carcinogens, such as ionizing radiation, can cause stromal fibroblasts to activate TGF beta by epigenetic mechanisms. As the biological effects of the anti-estrogen tamoxifen may well be mediated by TGF beta, this model has a number of important implications for the clinical uses of tamoxifen in the prevention and treatment of breast cancer. In addition, it suggests a number of novel approaches to the treatment of advanced breast cancer.", 
"The major cause of death from cancer is metastases that are resistant to conventional therapies. Several reasons account for treatment failure in patients with metastases. First, neoplasms are biologically heterogeneous and contain subpopulations of cells with different angiogenic, invasive, and metastatic properties. Second, the process of metastasis selects a small subpopulation of cells that preexist within a parental neoplasm. Although metastases can have a clonal origin, genetic instability results in rapid biological diversification and the regeneration of heterogeneous subpopulations of cells. Third, and perhaps the most important principle for the design of new cancer therapies, is that the outcome of metastasis depends on multiple interactions (cross-talk) of metastatic cells with homeostatic mechanisms which the tumor cells usurp. The organ microenvironment can influence the biology of cancer growth, angiogenesis, and metastasis in several different ways. For example, the survival and growth of tumor cells are dependent on angiogenesis, which is mediated by an imbalance between positive and negative regulating molecules released by tumor cells, normal cells surrounding a tumor, and infiltrating lymphoid cells. Many cytokines that stimulate or inhibit angiogenesis are present in different tissues, and thus the organ environment profoundly influences this process. Moreover, the organ microenvironment can also influence the response of metastases to chemotherapy by regulating the expression of different drug resistance genes, such as mdr-1. The finding that the resistance of metastases to some chemotherapeutic agents can be mediated by epigenetic mechanisms has obvious implications for therapy. The identification of organ-specific cytokines that can upregulate expression of mdr-1 (or other resistant mechanisms) may suggest an approach to overcome the resistance of some metastases to particular chemotherapeutic agents. Therefore therapy of metastasis should be targeted not only against metastatic tumor cells, but also the homeostatic factors that are favorable to metastasis, growth, and survival of the metastatic cells.", 
"Our laboratory has found genomic imprinting of a large genomic domain of human 11p15.5, identifying six imprinted genes within this domain: (a) insulin-like growth factor II (IGF-II), an important autocrine growth factor in a wide variety of malignancies; (b) H19, an untranslated RNA that is a putative growth suppressor gene regulating IGF-II; (c) p57(KIP2), cyclin-dependent kinase inhibitor that causes G(1)-S arrest; (d) K(V)LQT1, a voltage-gated potassium channel; (e) TSSC3, a gene that is homologous to mouse TDAG51, which is implicated in Fas-mediated apoptosis; and (f) TSSC5, a putative transmembrane protein-encoding gene, We hypothesize that 11p15 harbors a large domain of imprinted growth- regulatory genes that are important in cancer, Several lines of evidence support this hypothesis: (a) we have discovered a novel genetic alteration in cancer, loss of imprinting, which affects several of these genes, and is one of the most common genetic changes in human cancer; (b) we have found that the hereditary disorder Beckwith-Wiedemann syndrome, which predisposes to cancer and causes prenatal overgrowth, involves alterations in p57(KIP2), IGF-II, H19, and K(V)LQT1; (c) we have found both genetic (somatic mutation in Wilms' tumor) and epigenetic alterations (DNA methylation) in cancer; and (d) we can partially reverse abnormal imprinting using an inhibitor of DNA methylation, We propose a model of genomic imprinting as a dynamic developmental process involving a chromosomal domain. According to this model, cancer involves both genetic and epigenetic mechanisms affecting this imprinted domain and the genes within it.", 
"Keratin 8 (K8) and keratin 18 (K18) are the most common and characteristic members of the large intermediate filament gene family expressed in 'simple' or single layer epithelial tissues of the body. Their persistent expression in tumor cells derived from these epithelia has led to the wide spread use of keratin monoclonal antibodies as aids in the detection and identification of carcinomas. Oncogenes which activate ras signal transduction pathways stimulate expression of the K18 gene through transcription factors including members of the AP-1 (jun and fos) and ETS families. The persistent expression of K8 and K18 may reflect the integrated transcriptional activation of such transcription factors and, in the cases of ectopic expression, an escape from the suppressive epigenetic mechanisms of DNA methylation and chromatin condensation. Comparison of the mechanisms of transcriptional control of K18 expression with expression patterns documented in both normal and pathological conditions leads to the proposal that persistent K8 and K18 expression is a reflection of the action of multiple different oncogenes converging on the nucleus through a limited number of transcription factors to then influence the expression of a large number of genes including these keratins. Furthermore, correlation of various tumor cell characteristics including invasive behavior and drug sensitivity with K8 and K18 expression has stimulated consideration of the possible functions of these proteins in both normal development and in tumorigenesis. Recent developments in the analysis of the functions of these intermediate filament proteins provide new insights into diverse functions influenced by Kg and K18.", 
"The cell cycle regulatory genes p16/CDKN2 RE are frequently deleted in prostate cancers. In this study, We examined the role of alterations in p16 and pRb during growth, senescence, and immortalization in vitro of human prostate epithelial cells (HPECs), HPECs are established from normal prostate tissues and cultured on collagen-coated dishes, Our results show that p16 is reproducibly elevated at senescence in HPECs, HPECs are immortalized using human papilloma virus 16 E6 and/or E7 as molecular tools to inactivate p53 and/or pRb, respectively. Immortalization occurs infrequently in this system and only after a latent period during which additional genetic/epigenetic changes are thought to occur. Notably;, all of the E6-immortalized HPEC lines but none of the E7 lines show, inactivation oof p16/CDKN2 by deletion, methylation, or mutation in association with immortalization. In contrast, E7 lines, in which pRb function is abrogated bg E7 binding, retain the high levels of p16 observed at senescence. Thus, all lines show either a p16 or pRb inactivation. Analysis of six independent lines from metastatic prostate cancers reveals a similar loss of either p16 or pRb, Comparative genomic hybridization of HPECs shows that gains of chromosomes 5q, so, and 20 are nonrandomly associated with; bSpassing senescence (probability = 0.95). These results suggest that high levels of the cyclin-dependent kinase inhibitor p16 mediate senescence G(1), arrest in HPECs and that bypassing this block by a p16/pRb pathway alteration is required for immortalization in vitro and possibly tumorigenesis in vivo. Our results further indicate that inactivation of the p16/pRb pathway alone is not sufficient to immortalize HPECs and that additional genetic alterations are required for this process.", 
"Expression of the invasion/metastasis suppressor, E-cadherin, is diminished or lost in thyroid carcinomas. Yet, mutational inactivation of E-cadherin is rare. Herein, we show that this loss is associated with hypermethylation of the E-cadherin 5' CpG island in a panel of human thyroid cancer cell lines. This aberrant methylation is evident in 83% of papillary thyroid carcinoma, 11% of follicular thyroid carcinoma, 40% of Hurthle's cell carcinoma, and 21% of poorly differentiated thyroid carcinomas. Contrary to previous reports, the majority of these poorly differentiated thyroid carcinomas express E-cadherin, but often within the cytoplasm rather than at the cell surface. Together, our data indicate that the invasion/metastasis suppressor function of E-cadherin is frequently compromised in human papillary, Hurthle's cell, and pearly differentiated thyroid carcinoma by epigenetic and biochemical events.", 
"The development of a malignant tumor involves the progressive acquisition of mutations and epigenetic abnormalities in multiple genes that have highly diverse functions, Some of these genes code for pathways of signal transduction that mediate the action of growth factors, The enzyme protein kinase C plays an important role in these events and in the process of tumor promotion, Therefore, we examined the effects of three inhibitors of protein kinase C, CGP 41251, RO 31-8220, and calphostin C, on human glioblastoma cells, These compounds inhibited growth and induced apoptosis; these activities were associated with a decrease in the level of CDC2 and cyclin B1/CDC2-associated kinase activity, This may explain why the treated cells accumulated in G(2)-M. In a separate series of studies, we examined abnormalities in cell cycle control genes in human cancer, We have found that cyclin D1 is frequently overexpressed in a variety of human cancers, Mechanistic studies indicate that cyclin D1 can play a critical role in carcinogenesis because: overexpression enhances cell transformation and tumorigenesis; introduction of an antisense cyclin D1 cDNA into either human esophageal or colon cancer cells reverts their malignant phenotype; and overexpression of cyclin D1 can enhance the amplification of other genes, The latter finding suggests that cyclin D1 can enhance genomic instability and, thereby, the process of tumor progression, Therefore, inhibitors of the function of cyclin D1 may be useful in both cancer chemoprevention and therapy, We obtained evidence for the existence of homeostatic feedback loops between cyclins D1 or E and the cell cycle inhibitory protein p27(Kip1). On the basis of these and other findings, we hypothesize that, because of their disordered circuitry, cancer cells suffer from gene addiction and gene hypersensitivity, disorders that might be exploited in both cancer prevention and therapy.", 
"Spontaneous regression of cancer is reported in virtually all types of human cancer, although the greatest number of cases are reported in patients with neuroblastoma, renal cell carcinoma malignant melanoma and lymphomas/leukemias. Study of patients with these diseases has provided most of the data regarding mechanisms of spontaneous regression. Mechanisms proposed for spontaneous regression of human cancer include: immune mediation, tumor inhibition by growth factors and/or cytokines, induction of differentiation, hormonal mediation, elimination of a carcinogen, tumor necrosis and/or angiogenesis inhibition psychologic factors, apoptosis and epigenetic mechanisms. Clinical observations and laboratory studies support these concepts to a variable extent. The induction of spontaneous regression may involve multiple mechanisms in some cases although the end result is likely to be either differentiation or cell death. Elucidation of the process of spontaneous regression offers the possibility of improved methods of treating and preventing cancer.", 
"Recent evidence suggests that resistance to antineoplastic therapy may result from mutations in genes mediating the apoptotic response to DNA damage, To determine the effects of epigenetic changes on tumor responsiveness to cytotoxic agents inducing DNA damage, we examined the chemosensitivity of neuroblastoma (NB) after differentiation by retinoic acid (RA). Differentiation of the cell lines SH-SY5Y and SMS-KCNR by RA abolished the cytotoxic effects of adriamycin (Adr) and cisplatin. Chemoresistance was not the result of decreased proliferation induced by RA because: (a) growth arrest by nutrient deprivation did not affect sensitivity; (b) growth arrested NE cell lines, which did not differentiate, remained chemosensitive; and (c) RA concentrations which promoted differentiation without affecting growth, induced resistance, Apoptosis characterized NE cells responding to Adr, although differentiated SH-SY5Y did not apoptose and were resistant to Adr and cisplatin. Marked induction of bcl-2 in NE cells followed RA-induced differentiation, whereas in cell lines failing to differentiate, bcl-2 was not detected, Our data indicate that NE differentiation induces drug resistance after a loss of the apoptotic response to antineoplastic drugs and suggest that bcl-2 overexpression is an important mechanism of resistance in differentiated tumor cells.", 
"The few imprinted genes characterized so far include the insulin-like growth factor-2 gene (IGF2) coding for a foetal growth factor and the H19 gene whose normal function is unknown but which is likely to act as an RNA with an antitumour effect, IGF2 is expressed by the paternal allele and H19 by the maternal allele. This reciprocal expression is quite interesting because both H19 and IGF2 genes are located close to each other on chromosome 11p15.5 in a region subject to loss of heterozygosity (LOH), Moreover, loss of imprinting (LOI) or biallelic expression has been proposed as an epigenetic mechanism for tumorigenesis in a variety of human cancers including Wilms' tumour, In this study we report the LOH, LOI and methylation status of H19 and IGF2 genes in 29 invasive cervical carcinomas of different clinical stages, Fourteen (48%) and 13 (45%) tumours were heterozygous for H19 and IGF2 respectively, LOH for H19 and IGF2 genes were found in 2 of 14 (14%) and 3 of 13 (23%) informative tumours, respectively, LOI of H19 and IGF2 was detected in 2 of 12 (17%) and 5 of 10 (50%) tumours with no LOH, respectively, More interestingly, monoallelic expression of the otherwise silent H19 allele (allele switch) was observed in 2 of 12 (17%) tumours and biallelic expression of IGF2 was detected in one specimen of normal cervix adjacent to the tumour, The expressing H19 allele, and to a lower degree also the silent allele, were hypomethylated in tumours suggesting that demethylation of both H19 alleles may be associated with an early step of imprinting alteration. In cervical cancer H19 and IGF2 expressions could be independently regulated, In conclusion, our data suggest that H19 and IGF2 genes, via deletions and/or abnormal imprinting, could play a crucial role in a large proportion (58%) of cervical cancers where they may be associated with disease progression.", 
"Background: The identification in 1994 of the CDKN2 gene as a target for mutations in a wide range of human cancers, including malignant mesothelioma, has been controversial because subsequent studies have detected a lower frequency of CDKN2 gene mutations in primary tumors than in cultured cell lines, These reports raised the hypothesis that another gene, distinct from CDKN2, might be the target of the chromosome 9p21 deletions frequently observed in these tumors, Purpose: To address whether inactivation of CDKN2 function is an essential event in the etiology of malignant mesothelioma, we examined p16(INK4) protein expression in primary thoracic mesotheliomas, in nonmalignant pleural tissues, and in independent mesothelioma cell lines, We also studied the growth rate of tumor cell lines following stable transfection of CDKN2 gene, Methods: Retinoblastoma (Rb) and p16(INK4) protein expression was determined by immunohistochemical analysis from archival paraffin specimens of 12 primary thoracic mesotheliomas and a nonmalignant pleural biopsy specimen, In addition, protein immunoblot analysis for Rb and p16(INK4) expression was conducted on 15 independent mesothelioma cell lines, and the ability of a transfected CDKN2 gene to suppress the growth of the mesothelioma cell lines H2373 and H2461 in vitro was examined, Results: We demonstrated abnormal p16(INK4) expression in 12 of 12 primary mesothelioma specimens and in 15 of 15 mesothelioma cell lines, All tumor specimens and the tumor cell lines showed expression of wild-type Rb protein, In addition, we have confirmed the ability of a transfected CDKN2 gene to suppress growth of two independent mesothelioma cell lines, Conclusions: Immunohistochemical analysis of the p16(INK4) gene product is feasible in archival biopsy samples, With this analysis, CDKN2 gene inactivation can be determined in tumors that are contaminated with nonmalignant cells, Furthermore, since loss of p16(INK4) protein expression can result from both genetic (gene mutations) and epigenetic (abnormal DNA hypermethylation) mechanisms, as we and others have shown recently, examination of protein expression is a highly sensitive method for analyzing the CDKN2 status in large numbers of tumor samples, Implications: This study suggests that inactivation of the CDKN2 gene is an essential step in the etiology of malignant mesotheliomas, Defining the role of the p16(INK4):Rb tumor suppressor pathway and its immediate downstream substrates will be an important goal in designing future therapeutic strategies.", 
"The yeast Saccharomyces cerevisiae has a limited life span that can be measured by the number of times individual cells divide. Several genetic manipulations have been shown to prolong the yeast life span. However, environmental effects that extend longevity have been largely ignored. We have found that mild, nonlethal heat stress extended yeast life span when it was administered transiently early in life. The increased longevity was due to a reduction in the mortality rate that persisted over many cell divisions (generations) but was not permanent. The genes RAS1 and RAS2 were necessary to observe this effect of heat stress. The RAS2 gene is consistently required for maintenance of life span when heat stress is chronic or in its extension when heat stress is transient or absent altogether. RAS1, on the other hand, appears to have a role in signaling life extension induced by transient, mild heat stress, which is distinct from its life-span-curtailing effect in the absence of stress and its lack of involvement in the response to chronic heat stress. This distinction between the RAS genes may be partially related to their different effects on growth-promoting genes and stress-responsive genes. The ras2 mutation clearly hindered resumption of growth and recovery from stress, while the ras1 mutation did not. The HSP104 gene, which is largely responsible for induced thermotolerance in yeast, was necessary for life extension induced by transient heat stress. An interaction between mitochondrial petite mutations and heat stress was found, suggesting that mitochondria may be necessary for life extension by transient heat stress. The results raise the possibility that the RAS genes and mitochondria may play a role in the epigenetic inheritance of reduced mortality rate afforded by transient, mild heat stress. (C) 1998 Academic Press.", 
"We previously reported 9 unilateral, sporadic retinoblastomas with hypermethylation in the 5' region of the RE gene, and we found that CpG methylation in the RE promoter inhibits the binding of the retinoblastoma binding factor I (RBF-1) and the activating transcription factor (ATF)-like factors, thereby resulting in a considerable reduction in RE promoter activity. In this study, we screened for hypermethylation in 121 additional cases of retinoblastoma, and found 5 tumors with hypermethylation, including 4 unilateral, sporadic tumors, and one hereditary tumor. The hereditary tumor had a germline deletion of one allele, and the hypermethylation was an acquired, epigenetic change in the other allele. Another tumor had hypermethylation restricted to approximately 800 base pairs in the RS promoter region including the essential RBF-1 and A TF sites. The frequency of hypermethylation in unilateral, sporadic tumors was 9.3% combining our previous and present examinations (13 among 140), whereas the frequency was 1.0% in bilateral hereditary tumors (one among 101). The statistical analyses using the chi-square test indicated significant correlation between hypermethylation and unilateral, sporadic tumors (p < 0.05). These results suggest that hypermethylation in the RE gene is always an acquired, epigenetic change and causes about 9% of unilateral, sporadic tumors. (C) Elsevier Science Inc., 1997.", 
"To investigate the relationship between aberrant crypt foci (ACF) and colon neoplasia in colorectal carcinogenesis, we evaluated 433 ACF, which were collected from the grossly normal mucosa of surgical specimens from 57 patients with colorectal cancer. The ACF ranged in size from 3 to 412 aberrant crypts/focus. Large ACF (greater than or equal to 50 crypts/focus) comprised 25% of the total ACF studied. Histopathologically, 65% (67 of 103) of large ACF were diagnosed as hyperplasia, 10% (10 of 103) as adenoma, and 1% (1 of 103) as within normal colorectal mucosa. The remaining 24% (25 of 103) were diagnosed as ''stage I abnormality crypts,'' which were characterized by their extension of the proliferative compartment to the surface of crypts but with no changes in the major site of proliferation, as designated by E. E. Deschner [Pathol, Annu., 18 (Part 1): 205-219, 1983]. Of the 25 stage I abnormality ACF, 7 ACF coexisted with hyperplasia. Of 10 adenomatous ACF, two coexisted with stage I abnormality crypts, A K-ras codon 12 mutation was identified in 85% (93 of 109) of large ACF. The proliferative activity of stage I crypts was significantly higher than that of hyperplastic crypts in the same ACF. These observations suggest that some hyperplastic ACF may develop into adenomatous ACF by way of stage I abnormality ACF with concomitant acquisition of higher proliferative activity through some genetic and/or epigenetic changes.", 
"Several lines of evidence from our laboratory and others indicate that epigenetic alterations in protein kinase C (PKC) are involved in colonic carcinogenesis in both man and experimental animals. Furthermore, bile salts, known activators of PKC, have also been implicated in colonic tumor development. Recently, however, our laboratory has demonstrated that, whereas dietary cholic acid increased the occurrence of azoxymethane (AOM)-induced rat colonic tumors, ursodeoxycholic acid was associated with a significant protective effect. In the present studies, we therefore examined changes in PKC isoforms that accompanied AOM-induced tumor formation and investigated whether the chemopromotional and/or chemopreventional actions of these supplemental dietary bile salts involved changes in specific isoforms of PKC. Rats treated with vehicle (saline) or AOM and maintained on bile salt unsupplemented or supplemented diets were used to isolate control colonocytes and carcinogen-induced tumors, which were then subjected to subcellular fractionation. The homogenates and subcellular fractions mere then probed for individual PKC isoforms by quantitative Western blotting using isoform-specific antibodies. Normal rat colonocytes expressed PKC-alpha, -beta(II), -delta, -epsilon, and -zeta. AOM, in unsupplemented or cholate-supplemented groups, caused significant down-regulation of PKC-alpha, -delta and -zeta and up-regulation of PKC-beta(II) while increasing particulate PKC-alpha, -beta(II), and -zeta in carcinogen-induced tumors compared to normal colonocytes. Dietary supplementation with ursodeoxychohc acid, in marked contrast to these groups, prevented the changes in the subcellular distributions of PKC-alpha, -beta(II), and -zeta, and preserved the expression of PKC-zeta in AOM-induced tumors. These studies suggest that changes in specific isoforms of PKC (particularly, PCK-alpha, -beta(II), -delta, and/or -zeta) are involved in colonic malignant transformation in the AOM model but do not account for the chemopromotional actions of cholic acid in this model. furthermore, the ability of ursodeoxycholic acid to block AOM-induced increases in particulate PKC-alpha, -beta(II), and -zeta, and/or inhibit down-regulation of PKC-zeta, may contribute to the chemopreventive effects of this bile acid.", 
"The developmentally regulated H19 gene displays several remarkable properties: expression of an apparently non-translated mRNA, genomic imprinting (maternal allele only expressed), relaxation of the imprinting and/or epigenetic lesions demonstrated in some tumors. Despite several observations after relaxation of imprinting status of the gene, data on tr ans and cis-acting factors required for the human H19 gene expression are still missing. As a first approach to address identification of factors involved in the regulation of the gene, we found that cells from a p53 antisense-transfected HeLa clone displayed increased amounts of H19 transcripts when compared to the non-transfected cells. Moreover, a HeLa clone stably transfected with a temperature sensitive (ts) 143 Ala p53 mutant exhibited temperature-dependent regulation of H19 expression. This preliminary indication of the repressing effect of the p53 protein on H19 expression has been confirmed by transient cotransfection experiments in HeLa cells, using luciferase surrogate constructs under the control of the 823 bp sequence immediately upstream of the transcription start point of the H19 gene, and different constructs containing sense, antisense or a ts 143 Ala mutant p53 cDNA. We observed an increase of H19 promoter-driven activity in transient cotransfections with the antisense p53 cDNA and the temperature sensitive mutant p53 at the non-permissive temperature, but a decrease with sense wild-type p53 cDNA. Furthermore, the cotransfection experiments were repeated in a cell line lacking endogenous p53, (Calu 6 cells) and the results provided additional evidence for a down regulation of the expression of the H19 gene by the p53 protein.", 
"Gelsolin is a multifunctional, actin-binding protein that is greatly decreased in many transformed cell lines and tumor tissues, including breast cancers, Downregulation of gelsolin RNA occurs in most breast cancers of rats, mice, and humans, but gross mutations of the gelsolin gene have not been found. Here we demonstrate by PCR and RT-PCR analysis that there are no point mutations in putative regulatory regions or the entire coding region of the cytoplasmic isoform of the gelsolin gene in human breast cancer cells (BCC). To determine if epigenetic modification is involved in downregulating gelsolin expression in MDA-MB-231 (MDA231), MCF7, and T47D BCC, we have used Southern blot analysis, 5-azacytidine (5aza) treatment, and trichostatin A (TSA) treatment. Southern blot analysis performed on genomic DNA demonstrated altered CpG methylation within intron 1 in DNA from all BCC compared to normal, mortal human mammary epithelial cells (HMEC). Treatment of the BCC with 5aza converted the DNA restriction pattern to that seen in untreated HMEC genomic DNA and caused modest increases in gelsolin RNA and protein. Incubation with TSA, an inhibitor of histone deacetylase, induced a dramatic upregulation of gelsolin RNA and protein levels which preceded apoptotic death of all BCC within 48-60 h. Our data support a role for epigenetic changes in chromatin structure leading to downregulation of gelsolin expression in human breast cancer, To our knowledge, this is the first example of a tumor suppressor gene downregulated in human breast cancer by changes in histone acetylation. (C) 1999 Academic Press.", 
"Genomic DNA methylation patterns influence the development and maintenance of function during cellular differentiation. Methylation of regulatory sequences can have long-lasting effects on gene expression if inherited in an epigenetic manner. Recent work suggests that DNA methylation has a regulatory role in differential cytokine gene expression in primary T lymphocytes, Here we show, by clonal Lineage analysis, that methylation patterns in the IFN-gamma promoter exhibit long term faithful inheritance in CD44(high)CD8(+) T cells and their progeny, through 16 cell divisions and a clonal expansion of 5 orders of magnitude. Moreover, the demethylated IFN-gamma promoter is faithfully inherited following the withdrawal of T cell stimulation and the loss of detectable IFN-gamma mRNA, consistent with passive rather than active maintenance mechanisms. This represents a form of stable cellular memory, of defined epigenetic characteristics, that may contribute to the maintenance of T cell cytokine expression patterns and T cell memory.", 
"The presence of ETV6 deletions wats investigated in 215 children with acute lymphoblastic leukemia (ALL) using the loss of heterozygosity (LOH) approach. We used four intragenic or juxtagenic microsatellite markers to detect allelic deletions. In this series of unselected patients, LOH of ETV6 markers was found in 23% of cases (6% of T-ALL and 26% of B lineage ALL) confirming that chromosome 12p12-13 deletions represent a major genetic alteration in childhood ALL, frequently missed by cytogenetic analysis. The presence of a t(12;21)(p13;q22) was studied by RT-PCR and/or FISH in a total of 134 patients (125 B lineage ALL, nine T-ALL) including 42 cases with LOH. Thirty-four out of 44 patients (77%) for whom a t(12;21) was observed displayed LOH of the ETV6 markers. When associated with a t(12;21), ETV6 is very likely to be the target of deletions as indicated by the detection of intragenic deletions in three patients. Although deletion of ETV6 and t(12;21) were associated in most patients, in eight cases (six B lineage and two I-ALL) LOH was detected at the ETV6 locus without ETV6-AML1 hybrid RNA. FISH studies conducted in five of these eight patients confirmed the absence of translocation involving ETV6. In such patients, the other allele of ETV6 could be disrupted by either a small deletion, a point mutation, or an epigenetic modification and it will be of interest to study the! structure and expression of the remaining allele of ETV6 in these cases. Alternatively, a tumor suppressor gene located close to ETV6 and CDKN1B could be the target of deletions.", 
"The tumor suppressor genep53 encodes a nuclear phosphoprotein which is critical for cell cycle control and prevention of uncontrolled cell proliferation that can lead to cancer. Previous studies have shown that cells respond to DNA damage by increasing their levels of p53, which then acts to prevent replication of damaged DNA, This study examined the effects on p53 protein levels of several different categories of chemical carcinogens. N-Methyl-N' -nitro-nitrosoguanidine and N-ethyl-N-nitrosourea, two direct-acting genotoxic (DNA-reactive) carcinogens, caused p53 induction as early as 2 h following treatment, with peak increases within 4-12 h, Aflatoxin B-1 and 2-acetylaminofluorene, indirect-acting genotoxic carcinogens, caused a later induction of p53, with the peak increase appearing between 16 and 24 h following treatment. These observations demonstrate a correlation between p53 induction pattern and DNA damaging mechanism of genotoxins. Phenol, diethylstilbestrol and ethylacrylate also induced increases in cellular p53, The half-life of p53 protein was increased in cells treated with genotoxic agents, On the other hand, the epigenetic (non-DNA-reactive) carcinogens azathioprine and saccharin, as well as two substances generally considered to be non-carcinogens, dimetfiylsulfoxide and benzethonium chloride, had no effect on p53 protein levels of treated cells. Measurement of the cytotoxic effects of each of these chemicals led to the conclusion that p53 protein induction is not a general, non-specific consequence of the cytotoxic effect of these genotoxins, These results suggest that measurement of p53 protein induction may be an effective tool to identify environmental genotoxins.", 
"The two gene products of the CDKN2A gene, p16 and p19(ARF), have recently been linked to each of two major tumour suppressor pathways in human carcinogenesis, the RB1 pathway and the p53 pathway. p16 inhibits the phosphorylation of the retinoblastoma gene product by cyclin D-dependent kinases, whereas p19(ARF) targets MDM2, a p53 inhibitory protein, for degradation. A deletion of CDKN2A would therefore disturb both pathways. To explore the p53 pathway genes as a functional unit in diffuse large B cell non-Hodgkin's lymphomas (DLCL), we wanted to see whether there exists mutually exclusiveness of aberrations of CDKN2A, MDM2 and p53, since this has not been analysed previously. We investigated 37 DLCL for aberrations of p15, p16, p19(ARF), MDM2, and p53 at the epigenetic, genetic and/or protein levers. Homozygous deletion of CDKN2A was detected in seven (19%) of 37 tumours, and another three cases were hypermethylated at the 5' CpG island of p16. No point mutations were found in CDKN2B or CDKN2A. immunohistochemical staining of formalin-fixed, paraffin-embedded tissue for p16 confirmed these results, as all tumours with alterations of CDKN2A were pie immunonegative. We found p53 mutations in eight (22%) cases and MDM2 overexpression in 16 (43%) tumours. Twenty-three (62%) tumours had alterations of one or more p53 pathway components (p53, p19(ARF) and MDM2). Furthermore, 7/9 (78%) p16-immunonegative tumours showed co-aberration of p53 and/or MDM2. The lack of correlation between these aberrations suggests that DLCL acquire additional growth advantage by inactivating both of these critical regulatory pathways.", 
"Thromboxane A(2) is a biologically potent arachidonate metabolite through the cyclooxygenase pathway. It induces platelet aggregation and smooth muscle contraction and may promote mitogenesis and apoptosis of other cells. Its roles in physiological and pathological conditions have been widely documented. The enzyme that catalyzes its synthesis, thromboxane A(2) synthase, and the receptors that mediate its actions, thromboxane A(2) receptors, are the two key components critical for the functioning of this potent autacoid. Recent molecular biological studies have revealed the structure-function relationship and gene organizations of these proteins as well as genetic and epigenetic factors modulating their gene expression. Future investigation should shed light on detailed molecular signaling events specifying thromboxane A(2) actions, and the genetic underpinning of the enzyme and the receptors in health and disease.", 
"Carcinogenesis proceeds in discrete steps involving initiation and promotion, There is ample evidence that the underlying cause of initiation is mutation, whereas for tumor promotion different hypotheses exist postulating the involvement of both epigenetic and genetic changes, DNA repair protects against tumor formation, but it has not been proven whether protection occurs at the level of tumor initiation or promotion, Since the most advanced experimental system for studying multistep carcinogenesis is the mouse skin, we generated transgenic mice that overexpress the human DNA repair protein O-6-methylguanine-DNA methyltransferase (MGMT) in their epidermal cells by virtue of cytokeratin (Ck) promoters, Total cellular methyltransferase activity was found to he significantly higher in skin protein extracts of transgenic as compared to nontransgenic mice, CkMGMT transgenic mice along with nontransgenic controls were treated according to the multistage skin carcinogenesis protocol. For initiation, a single subthreshold dose of N-nitroso-N-methylurea (MNU) or 7,12-dimethylbenz(a)anthracene (DMBA) was topically applied to the dorsal skin of the mice, Tumor promotion was carried out by repeated 12-O-tetradecanoylphorbol-13-acetate application, Our results clearly show that CkMGMT transgenic mice are strongly protected against MNU- but not DMBA-initiated skin tumor formation, As compared to nontransgenic controls, transgenic mice exhibited an approximately 6-fold reduction of skin tumor incidence after treatment with 20 mu mol or 50 mu mol MNU followed by 12-O-tetradecanoylphorbol-13-acetate. These results provide direct and the most compelling evidence to date that the DNA lesion O-6-methylguanine is of decisive importance in tumor initiation, and that the protective effect of the repair protein MGMT in carcinogenesis is due to prevention of initiation without affecting tumor promotion.", 
"Relaxation of IGF2 imprinting occurs in Wilms tumours and many other cancers, but the mechanism of loss of imprinting (LOI) remains unknown. To investigate the role of altered DNA methylation in LOI, we examined the pattern of methylation of the human insulin-IGF2 region in Wilms tumours and the normal kidney. The analysis included regions homologous to three 'differentially methylated regions' of the mouse Igf2 gene (dmrs 0, 1 and 2), In tumours displaying normal IGF2 imprinting, and in the normal kidney, maternal allele-specific DNA methylation was identified spanning exons 2 and 3, This region is homologous to dmr 0, a site of maternal-specific differential methylation in the mouse. In Wilms tumours with relaxed imprinting or 11p15.5 LOH this region was unmethylated. No other differential methylation was identified, In particular, two sites of paternal methylation in the mouse (dmrs 1 and 2), and all three imprinted IGF2 promoters were not methylated in the kidney or in Wilms tumours, We postulate that LOI in Wilms tumours is associated with loss of maternal allele-specific methylation from a region located upstream of the imprinted IGF2 promoters, This region may contain cis acting sequences that coordinately influence imprinting.", 
"Disseminated disease, especially to the liver, constitutes the major risk of recurrence for colorectal cancer patients. However, successful resection can still be achieved in 25-35% of colorectal cancer patients with isolated metastases, To evaluate the clinical value of occult micrometastatic disease detection in lymph nodes, we tested genetic (K-ras and p53 gene mutations) and epigenetic (p16 promoter hypermethylation) molecular markers in the perihepatic lymph nodes from colorectal cancer patients with isolated liver metastases, DNA was extracted from 21 paraffin-embedded liver metastases and 80 lymph nodes from 21 colorectal cancer patients. K-ras and p53 gene mutations were identified in DNA from liver metastases by PCR amplification followed by cycle sequencing. A sensitive oligonucleotide-mediated mismatch ligation assay was used to search for the presence of K-ras and p53 mutations to detect occult disease in 68 lymph nodes from tumors positive for these gene mutations. Promoter hypermethylation at the pld tumor suppressor gene was examined in both liver lesions and lymph nodes by methylation-specific PCR, Sixteen of the 21 (76%) liver metastases harbored either gene point mutations or p16 promoter hypermethylation, Twelve of the 68 lymph nodes were positive for tumor cells by molecular evaluation and negative for tumor cells by histopathology and cytokeratin immunohistochemistry, whereas none were positive for tumor cells by histopathology or negative for tumor cells by molecular analysis (P = 0.0005, McNemar's test). Moreover, in three patients with lymph nodes that were histologically negative at all sites, molecular screening detected tumor DNA at one or more lymph nodes. Survival analysis shelved a median survival of 1056 days for patients without evidence of lymph node involvement by molecular analysis and 165 days for patients with positive lymph nodes by this approach (P = 0.0005), These results indicate that lymph node metastasis screening in colorectal cancer patients by molecular-based techniques increases the sensitivity of tumor cell detection and can be a good predictor of recurrence in colorectal cancer patients with resectable liver metastases.", 
"Epigenetic mechanisms may be the main driving force for critical changes in gene expression that are responsible for progression of prostate cancers. The three most extensively characterized mechanisms for epigenetic gene-regulation are (i) changing patterns of DNA methylation, (ii) histone acetylations/deacetylations, and (iii) alterations in regulatory feedback loops for growth factors. Several studies have indicated that DNA hypermethylation is an important mechanism in prostate cancer for inactivation of key regulatory genes such as E-cadherin, pi-class glutathione S-transferase, the tumor suppressors CDKN2 and PTEN, and IGF-II. Similarly, histone acetylations and deacetylations are frequently associated respectively with transcriptional activation (e.g. IGFBP-2 and p21) and repression (e.g. Mad:Max dimers) of genes linked to prostate cancer progression. Recently, histone acetyltransferase and deacetylase activities have been shown to be intrinsic with transcriptional coregulator proteins that bind to steroid receptors (e.g. SRC-1 and PCAF). Changes in regulatory feedback loops for growth factors with prostate cancer progression tend toward shifts from paracrine to autocrine control where the receptor and ligand are produced by the same cell. While there are several examples of this progression pattern in prostate tumors such as with IGF, FGF, TGF-alpha and their respective receptors, the precise mechanism (i.e. epigenetic or mutational) is less certain. In the context of treatment options, the contribution of mutational versus epigenetic events to prostate cancer progression is an improtant consideration. Irreversible genetic changes are likely to be less amenable to therapeutic control than are epigenetic ones.", 
"This review highlights current knowledge of environmental factors in carcinogenesis and their cellular targets. The hypothesis that environmental factors influence carcinogenesis is widely supported by both epidemiological and experimental studies. The fact that only a small fraction of cancers can be attributed to germline mutations in cancer-related genes further buttresses the importance of environmental factors in carcinogenesis, Furthermore, penetrance of germline mutations may be modified by either environmental or other genetic factors. Examples of environmental factors that have been associated with increased cancer risk in the human population include chemical and physical mutagens (e.g. cigarette smoke, heterocyclic amines, asbestos and UV irradiation), infection by certain viral or bacterial pathogens, and dietary nongenotoxic constituents (e.g. macro- and micronutrients), Among molecular targets of environmental influences on carcinogenesis are somatic mutation (genetic change) and aberrant DNA methylation (epigenetic change) at the genomic level and post-translational modifications at the protein level. At both levels, changes elicited affect either the stability or the activity of key regulatory proteins, including oncoproteins and tumor suppressor proteins. Together, via multiple genetic and epigenetic lesions, environmental factors modulate important changes in the pathway of cellular carcinogenesis.", 
"DNA methylation is now recognized as an important mechanism regulating different functions of the genome; gene expression, replication, and cancer, Different factors control the formation and maintenance of DNA methylation patterns. The level of activity of DNA methyltransferase (MeTase) is one factor. Recent data suggest that some oncogenic pathways can induce DNA MeTase expression, that DNA MeTase activity is elevated in cancer, and that inhibition of DNA MeTase can reverse the transformed state. What are the pharmacological consequences of our current understanding of DNA methylation patterns formation! This review will discuss the possibility that DNA MeTase inhibitors can serve as important pharmacological and therapeutic tools in cancer and other genetic diseases.", 
"The mouse skin model of multistage carcinogenesis has for many years provided a conceptual framework for studying carcinogenesis mechanisms and potential means for inhibiting specific stages of carcinogenesis. The process of skin carcinogenesis involves the stepwise accumulation of genetic change ultimately leading to malignancy. Initiation, the first step in multistage skin carcinogenesis involves carcinogen-induced genetic changes. A target-gene identified for some skin tumor initiators is c-Ha-ras. The second step, the promotion stage, involves processes whereby initiated cells undergo selective clonal expansion to form visible premalignant lesions termed papillomas. The process of tumor promotion involves the production and maintenance of a specific and chronic hyperplasia characterized by a sustained cellular proliferation of epidermal cells. These changes are believed to result from epigenetic mechanisms such as activation of the cellular receptor, protein kinase C, by some classes of tumor promoters. The progression stage involves the conversion of papillomas to malignant tumors, squamous cell carcinomas. The accumulation of additional genetic changes in cells comprising papillomas has been correlated with tumor progression, including trisomies of chromosomes 6 and 7 and loss of heterozygosity. The current review focuses on the mechanisms involved in multistage skin carcinogenesis, a summary of known inhibitors of specific stages and their proposed mechanisms of action, and the relevance of this model system to human cancer.", 
"Carcinogenesis is a multistage process driven by carcinogen-induced genetic and epigenetic damage in susceptible cells that gain a selective growth advantage and undergo clonal expansion as the result of activation of protooncogenes and/or inactivation of tumor suppressor genes. Therefore, the mutational spectra of chemical and physical carcinogens in these critical genes are of interest to define endogenous and exogenous mutational mechanisms. The p53 tumor suppressor gene is ideally suited for analysis of the mutational spectrum. Such an analysis has revealed evidence for both exogenous and endogenous molecular mechanisms of carcinogenesis. For example, an informative p53 mutational spectrum of frequent G --> T transversions in codon 249 is found in hepatocellular carcinomas from either Qidong, People's Republic of China, or southern Africa. This observation links exposure to aflatoxin B1, a known cancer risk factor in these geographic regions, with a specific mutation in a cancer-related gene. Other studies indicate that abnormalities in genes controlling the cell cycle may cause genomic instability and increase the probability of neoplastic transformation. Finally, mechanistic understanding of carcinogenesis is leading to improved cancer risk assessment and to the identification of individuals at high cancer risk.", 
"Background: Estrogens are potent mammary tumor promoters influencing post-initiational events via epigenetic mechanisms. The upregulation (i.e., induction) of the C16-alpha-hydroxylation pathway during 17-beta-estradiol (E2) biotransformation has been associated with mammary cell transformation. The action of E2 metabolites on tumorigenic transformation, however, is poorly understood. Purpose: The newly established mammary epithelial cell line C57/MG, derived from the C57BL mouse strain, was used to examine whether E2 or its metabolites, 16-hydroxyestrone (16-alpha-OHE1) and estriol (E3), function as initiators of mammary cell transformation. Methods: DNA repair (hydroxyurea-insensitive thymidine uptake), estrogen metabolism (H-3 exchange to form (H2O)-H-3), hyperproliferation (increased cell number), and acquisition of anchorage-independent growth (soft-agar colonies) were used as quantitative end points to measure the relative extent of transformation. Results: Treatment of cells with 200 ng/mL 16-alpha-OHE1 resulted in a 55.2% increase in DNA repair synthesis, a 23.09% increase in proliferative activity, and a 18-fold increase in the number of soft-agar colonies, relative to the solvent controls (P < .0001). The extent of upregulation of the three end points was similar to that induced by the genotoxic mammary carcinogen 7, 12-dimethylbenz[a]anthracene (DMBA, positive control). DMBA treatment also upregulated the ratio of 16-alpha/C2 hydroxylation of E2 leading to increased formation of 16-alpha-OHE1. E2 and E3 were not effective in upregulating these markers for transformation. Conclusion: These results demonstrate that in nontransformed C57/MG cells, 16-alpha-OHE1 may function as an initiator, perturbing the intermediate biomarkers for preneoplastic transformation.", 
"Environmental, occupational, and recreational exposures to carcinogens contribute to cancer risk in humans. Cancer formation is a multistage process involving tumor initiation, promotion, conversion, and progression. Carcinogens can affect any of these stages through genetic and epigenetic mechanisms. The association of a suspected carcinogenic exposure and cancer risk can be studied in populations with classic epidemiologic techniques. However, these techniques are not applicable to the assessment of risk in individuals. Molecular epidemiology, in contrast, is a field that integrates molecular biology, in vitro and in vivo laboratory models, biochemistry, and epidemiology to infer individual cancer risk. Carcinogen-macromolecular adduct levels, and somatic cell mutations can be measured to determine the biologically effective dose of a carcinogen. Molecular epidemiology also explores host cancer susceptibilities, such as carcinogen metabolic activation, DNA repair, endogenous mutation rates, and inheritance of mutated tumor suppressor genes. Substantial interindividual variation for each of these biologic end points has been shown and, therefore, highlights the need for assessing cancer risk on an individual basis. Given the pace of the last decade, it is feasible that the next 10 years will allow molecular epidemiologists to develop a cancer-risk profile for an individual that includes assessment of a number of factors. This will help focus preventive strategies and strengthen quantitative risk assessments.", 
"Background. Global DNA hypomethylation has been observed in some human neoplasms and has been implicated as an important factor in carcinogenesis. The current study was designed to assess whether DNA hypomethylation occurs in cervical dysplasia and cancer, and to determine the relationship between the degree of DNA hypomethylation and the grade of neoplasia. Methods. Cervical biopsy specimens were obtained from colposcopically identifiable lesions in 41 patients with abnormal Pap smear results. The extent of global DNA methylation was assessed by incubating the extracted DNA with [H-3]-S-adenosylmethionine and Sss1 methyltransferase, an enzyme that specifically catalyzes the transfer of methyl groups to cytosine residues in the cytosine-guanine doubler. The degree of exogenous H-3-methyl group incorporation into the DNA therefore is related reciprocally to the extent of endogenous DNA methylation. These data were compared with the histopathologic classification of the lesions. Results. The extent of H-3-methyl group incorporation was increased threefold and sevenfold in the DNA from cervical dysplasia and cancer, respectively, compared with the DNA from normal cervical tissue (P = 0.006, analysis of variance). Significant incremental increases in DNA hypomethylation were observed in the progression from normal and low grade squamous intraepithelial lesions (SIL) to high grade SIL and to cancer (P < 0.0001,trend). Conclusions. These data show that global DNA hypomethylation is a significant epigenetic event in cervical carcinogenesis and that the degree of DNA hypomethylation increases with the grade of cervical neoplasia. These data suggest that global DNA methylation may serve as a biochemical marker of cervical neoplasia.", 
"Intestinal metaplasia in the stomach increases the risk of gastric cancer, and the increased risk is proportional to the extent of the metaplasia. This risk could be generated by one or more mechanisms: (1) the metaplastic tissue is an early step in a multistep induction process; (2) the metaplastic tissue is an epigenetic change that raises the pH of gastric juice by replacing oxyntic mucosa, favoring the growth of a bacteria capable of generating endogenous mutagens; and/or (3) the metaplasia is only a marker for chronic gastritis due to H. pylori infection or pernicious anemia. With the last mechanism, the inflammatory response favors intramural mutagenesis that might result in metaplasia or neoplasia as independent events. Finding gene rearrangements common to both metaplastic and neoplastic tissue may establish a direct link between them, but too few have been identified to account for the large number of stomach cancers that develop in high risk populations. Histochemical and immunochemical stains that identify enzymes or mucosubstances may suggest that metaplastic epithelial cells resemble small or large intestinal cells, but they are distinctly different from both. Moreover, these stains do not indicate whether a given cytologic change is genetic or epigenetic; therefore, they cannot be used to define the relationship between metaplasia and neoplasia. It is unnecessary for practicing physicians to await resolution of this question. It can be assumed that any person with extensive metaplasia is at high risk for gastric cancer and should be subject to periodic screening. The extent of the metaplastic process is probably more important than the metaplastic subtype.", 
"Immunocytochemistry (ICC) has been used routinely to stain for p53 overexpression in a range of human tumours. The underlying assumption has been that positive staining indicates a mutation in the p53 coding sequence. Recently, however, discordancy has been observed and the accuracy of ICC as a marker of p53 gene mutation has been questioned. In this study of 109 colorectal adenocarcinomas, we compared ICC staining with p53 gene mutations detected by single-strand conformation polymorphism (SSCP) analysis. Concordancy between the two techniques was found in 69% of tumours. ICC-positive/SSCP-negative cases accounted for 20% of rumours and ICC-negative/SSCP-positive cases for the remaining 11%. These results caution against the assumption that p53 protein overexpression is always associated with a gene mutation. Epigenetic phenomena may account for a significant proportion of ICC-positive tumours.", 
"The outcome of cancer metastasis depends on the interaction of metastatic cells with various host factors. The implantation of human cancer cells into anatomically correct (orthotopic) sites in nude mice can be used to ascertain their metastatic potential. While it is clear that vascularity and local immunity can retard or facilitate tumor growth, we have found that the organ environment also influences tumor cell functions such as production of degradative enzymes. The organ microenvironment can also influence the response of metastases to chemotherapy. It is not uncommon to observe the regression of cancer metastases in one organ and their continued growth in other sites after systemic chemotherapy. We demonstrated this effect in a series of experiments using a murine fibrosarcoma, a murine colon carcinoma, and a human colon carcinoma. The tumor cells were implanted subcutaneously or into different visceral organs. Subcutaneous tumors were sensitive to doxorubicin (DXR), whereas lung or liver metastases were not. In contrast, sensitivity to 5-FU did not differ between these sites of growth. The differences in response to DXR between s.c. tumors (sensitive) and lung or liver tumors (resistant) were not due to variations in DXR potency or DXR distribution. The expression of the multidrug resistance-associated P-glycoprotein as determined by flow cytometric analysis of tumor cells harvested from lesions in different organs correlated inversely with their sensitivity to DXR: increased P-glycoprotein was associated with overexpression of mdr1 mRNA. However, the organ-specific mechanism for upregulating mdr1 and P-glycoprotein has yet to be elucidated.", 
"The genetic and epigenetic effects of nutritional folate deficiency were studied in two Chinese hamster ovary (CHO) cell Lines. The CHO-ABS cell line (hemizygous at the aprt locus) and CHO-UV5 (DNA repair-deficient mutant of AA8) were cultured in Ham's F-12 medium or in custom-prepared Ham's F-12 medium lacking foIic acid, thymidine, and hypoxanthine. Cells cultured acutely in the folate deficient medium exhibited initial growth arrest, followed by massive cell death and DNA fragmentation into nucleosomal multimers characteristic of apoptosis. Although prolonged culture in the folate deficient medium was cytostatic and lethal to the majority cells, minor subpopulations in both cell lines failed to initiate cell death, exhibited phenotypic abnormalities, and adapted a selective growth advantage under marginal folate conditions. These ''resistant'' clones exhibited major alterations in deoxynucleotide pools associated with an increase in mutant frequency at the aprt locus as detected by resistance to cytotoxicity in 8-azaadenosine. The mutation frequency in the DNA repair-deficient CHO-UV5 cells was similar to 100-fold greater than that in the parental AA8 clones, underscoring the importance of DNA repair under conditions of folate deficiency and nucleotide pool imbalance. The enhanced mutation frequency in the DNA repair-competent folate-deficient CHO-BAS cells suggests that DNA repair activity is less effective under folate-deficient conditions. These results add to the accumulating clinical and experimental evidence relating chronic folate deficiency to genomic instability and carcinogenesis.", 
"The demand for taxol, a promising cancer chemotherapeutic agent, far exceeds supply. Presently, taxol is derived from the bark of the Pacific yew, Taxus brevifolia, a small, slow-growing evergreen tree native to the northwestern United States. Knowledge of the distribution and magnitude of genetic and non-genetic sources of variation in taxol content in the genus Taxus is necessary if supply issues are to be met through plant harvesting. Analytical determinations of taxol, cephalomannine, and baccatin III in more than 200 trees representing several populations of T. brevifolia and other yew taxa indicate that (1) significant variation in taxane content exists among and within populations and species, (2) taxol levels exceeding those reported for T. brevifolia bark were found in shoots of individual trees from most taxa studied, and (3) the season in which samples are collected and handling procedures can influence taxane content.", 
"During the evolution of single-celled organisms to multi-cellular metazoans, a family of highly conserved genes coding for proteins (connexins), which as hexameric units (connexons), has evolved to form intercellular channels (gap junctions). These gap junctions allow ions and small molecular weight molecules to flow between coupled cells, thereby facilitating synchronization of electrotonic or metabolic cooperation. Control of cell proliferation, cell differentiation and adaptive responses of differentiated cells have been speculated to be biological roles of gap junctions. The regulation of these gap junctions can occur at the transcriptional, translational and posttranslational levels. Transient downregulation by endogenous or exogenous chemicals can bring about adaptive or maladaptive consequences depending on circumstances. Stable abnormal regulation of gap junction function has been associated with the activation of several oncogenes. Several tumor suppressor genes have also been associated with the up-regulation of gap junction function. Since gap junctions exist in all organs of the multi-cellular organisms, the dysfunction of these gap junctions by various toxic chemicals which have cell type/tissue/organ specificity could bring about very distinct clinical consequences, such as embryo lethality or teratogenesis, reproductive dysfunction in the gonads, neurotoxicity of the CNS system, hyperplasia of the skin, and tumor promotion of initiated tissue. understanding how many non-mutagenic chemicals might alter normal gap junction function should form the basis of ''epigenetic'' toxicology. On the other hand, restoring normal gap junction function to cells which have dysfunctional intercellular communication could be the basis for a new approach for therapeutic pharmaceuticals.", 
"Carcinogenesis in mouse skin can be divided into three distinct stages: initiation, promotion, and progression (malignant conversion). Initiation, induced by a single exposure to a genotoxic carcinogen, can result from a mutation in a single critical gene (e.g., ras(Ha)), apparently in only a few epidermal cells. The change is irreversible. Promotion, resulting in the development of numerous benign tumors (papillomas), is accomplished by the repeated application of a nonmutagenic tumor promoter. The effects of single applications of tumor promoters are reversible since papillomas do not develop after insufficient exposure of initiated skin to promoters or when the interval between individual promoter applications is increased sufficiently. The reversibility of promotion suggests an epigenetic mechanism. Promoter treatment provides an environment that allows the selective clonal expansion of foci of initiated cells. The conversion of squamous papillomas to carcinomas (termed progression or malignant conversion) occurs spontaneously at a low frequency. The rate of progression to malignancy can be significantly increased by treatment of papilloma-bearing mice with certain genotoxic agents. These progressor agents or converting agents are likely to act via a second genetic change in papillomas already bearing the initiating mutation. Progression in the skin is characterized by genetic changes that result in several distinct changes in the levels or activity of structural proteins, growth factors, and proteases. The mechanisms involved in progression are being studied in epidermal cell culture. In order to determine the in vivo phenotype of cultured cells, a grafting system was developed in which the cells were transferred from culture to a prepared skin bed in athymic mice. Introduction of an activated v-fos oncogene into initiated cells bearing an activated ras(Ha) gene produced cells with a carcinoma phenotype, i.e., carcinomas formed when the cells were grafted as part of reconstituted skin. Grafted keratinocytes containing the ras(Ha) gene alone produced papillomas; with v-fos alone, normal skin formed when grafted. The ras(Ha)/fos carcinomas showed changes in differentiation markers characteristic of chemically induced carcinomas. A cell culture assay utilizing cells initiated by the introduction of an activated ras(Ha) oncogene was developed to study progression. After exposure of initiated cells to progressor agents under conditions in which the proliferation of the ras(Ha)-initiated cells was suppressed, proliferating foci developed, with a good correlation of activity in the assay with activity in the progression stage in vivo. The cell culture assay provides a quantitative model to study chemically induced neoplastic progression and may be useful to identify potential progressor agents.", 
"Over-expression and abnormal intracellular location of the product of the oncogene c-myc in colonic dysplasia and neoplasia may be related to alterations in epigenetic mechanisms controlling the functioning of this gene. We have investigated the methylation patterns of the c-myc oncogene in human colorectal tissue representing various stages of dysplasia and neoplasia, including metastasis to liver, omentum and lymph node. Comparison of normal and neoplastic tissues from the same patient showed a decrease in methylation in a specific CCGG site in the third exon of c-myc through the progression from normal via dysplastic to neoplastic and metastatic tissue. Quantitative analysis revealed that in colonic adenocarcinomas an average of 66.1% and in metastatic deposits 83.1% of the myc gene DNA was hypomethylated at this site, as compared to a value of 9.2% in normal colonic mucosa. Adenomatous polyps showed an average value of 50.5% and hyperplastic polyps, 24.8%. The results suggest that partial hypomethylation of the c-myc gene third exon is associated with cell proliferation, and that deregulation of proliferation may be linked to the high levels of hypomethylation, presumably involving both copies of the gene in some cells, which occur at a relatively early stage in neoplastic progression.", 
"Despite the plethora of ''oncogenes'' and ''tumor suppressor genes,'' the hypothesis that cancer is usually the result of genomic mutations may be wrong. We should at least examine the alternative hypothesis, for which there is considerable evidence, that mutations do not commonly beget cancer, but rather that cancer phenotypes result from confused or aberrant patterns of normal-gene expression; the abnormal patterns are postulated to result from epigenetic mechanisms rather than from mutations. The epigenetic hypothesis that I am proposing suggests that cancers may exhibit mutations primarily because replicative errors at inactive sites in the cancer genome may he repaired slowly or not at all, but the mutations so produced, occurring at already inactivated sites in the genome, may have limited biological significance. Thus, it may be more correct to say that cancers beget mutations than it is to say that mutations beget cancers.", 
"Cells possess within their repertoire of epigenetic programs the ability to undergo a process of cellular suicide, termed programmed cell death. This programmed cell death process involves an epigenetic reprogramming of the cell that results in an energy-dependent cascade of biochemical and morphologic changes within the cell (also termed apoptosis), resulting in its death and elimination. Although the final steps (i. e. DNA and cellular fragmentation) are common to cells undergoing programmed death, the activation of this death process is initiated either by sufficient injury to the cell induced by various exogenous damaging agents (e.g. radiation, chemicals, viruses etc) or by changes in the levels of a series of endogenous signals (e.g. hormones and growth/survival factors). As an illustrative example, the role of androgen as a cell type specific endogenous regulator of the programmed death of normal and neoplastic prostatic cells will be presented.", 
"Fibroblasts are important contributors to both benign and malignant growth of prostate epithelial cells in vivo. In the human prostate cancer model that we have established, we can grow human LNCaP tumors reproducibly in athymic mice by coinoculating the animals with human LNCaP epithelial cells plus fibroblasts derived from either the prostate or bone; human lung, normal rat kidney, and embryonic mouse fibroblasts were inactive. We have delivered conditioned medium isolated from competent fibroblasts directly to sites where the tumor cells were injected and found that the conditioned medium alone confers tumorigenicity. Further studies of the mechanism of fibroblast-epithelial interaction have indicated that close metabolic cooperation between fibroblast and epithelial cells, involving the production of growth factors by the epithelial cells and the production of extracellular matrices and growth factors by the fibroblasts (assayed in vitro), is important in promoting prostate tumor growth in vivo. We have also investigated the possible in vivo interaction between extracellular matrix proteins such as laminin, collagens, heparan sulfate proteoglycans and Matrigel and prostate epithelial cells. Selective extracellular-matrix components were found to confer tumorigenicity to the prostate epithelial cells. Moreover, extracellular-matrix components were observed to induce cancer cell differentiation and alter permanently the morphology, gene expression and tumorigenic potential of the cancer epithelial cells.", 
" ", 
"Butylated hydroxyanisole (BHA) is a synthetic food antioxidant used to prevent oils, fats and shortenings from oxidative deterioration and rancidity. This review depicts the current knowledge on BHA. The physical and chemical characteristics of BHA are summarized and its function as a food antioxidant is made clear. The toxicological characteristics of BHA and its metabolic fate in man and animal are briefly reviewed. Special emphasis is laid on the carcinogenicity of BHA in the forestomach of rodents and to related events in the forestomach and other tissues in experimental animals. At present there is sufficient evidence for carcinogenicity of BHA, but there is hardly any indication that BHA is genotoxic. Therefore risk assessment for this epigenetic carcinogen is based on non-stochastic principles. However, the mechanism underlying the tumorigenicity of BHA is not known. In the last part of this review an attempt is made to unravel the unknown mechanism of carcinogenicity. It is hypothesized that BHA gives rise to tumor formation in rodent forestomach by inducing heritable changes in DNA. Evidence is being provided that reactive oxygen species, in particular hydroxylradicals, may play a crucial role. The key question with respect to risk assessment for BHA is whether or not the underlying mechanism is thresholded, which is important for the choice of the appropriate model to assess the risk, if any, for man and to manage any potential risk.", 
"Critical phenotypic changes that occur during the progression of breast cancer include the loss of hormone-dependence, acquired resistance to systemic therapies, and increased metastatic potential. We have isolated a series of MCF-7 human breast cancer variants which exhibit hormone-independent growth, antiestrogen resistance, and increased metastatic potential. Analysis of the phenotypes of these variants strongly suggests that changes in the expression of specific genes may be critical to the generation of phenotypic diversity in the process of malignant progression in breast cancer. Epigenetic changes may contribute significantly to the generation of these phenotypic changes observed during breast cancer progression. Many of the characteristics of the progressed phenotypes appear to have arisen in response to appropriate selective pressures (growth in ovariectomized nude mice: growth in the presence of antiestrogens). These observations are consistent with the concept of clonal selection and expansion in the process of malignant progression.", 
"In the present study, the possible role of the polyunsaturated fatty acids linoleic and arachidonic acid in the chemical induction of carcinogenesis has been investigated. Analysis of 7,8-dihydro-8-oxo-2'-deoxyguanosine (8-oxodG) levels in 2'-deoxyguanosine (dG) and isolated DNA has demonstrated that linoleic and arachidonic acid are capable of inducing this specific genotoxic damage. This effect appears to be related to the degree of fatty acid unsaturation, since it was not induced by monounsaturated oleic acid. Enzymatic peroxidation of linoleic and arachidonic acid resulted in a significant increase in oxidative DNA damage. Studies on the interference of radical scavengers with the induction of 8-oxodG in combination with electron spin resonance spectroscopy demonstrated that the superoxide anion was generated during peroxidation of these fatty acids and that singlet oxygen is most likely involved in the formation of oxidative DNA damage. The level of oxidative damage in dG and single-stranded DNA was higher as compared to that in native DNA after equimolar treatment. Exposure of human lymphocytes to linoleic or arachidonic acid did not result in a significant increase in levels of 8-oxodG. This may indicate that the rate of intracellular peroxidation is relatively low and/or that nuclear DNA in intact cells is effectively protected against genetic damage induced by reactive oxygen species. It is therefore concluded that relatively short periods of linoleic or arachidonic acid administration are not likely to impose a direct genotoxic risk. It can, however, not be excluded that chronic exposure to polyunsaturated fatty acids induces oxidative DNA damage or is related to cancer risk by epigenetic mechanisms, as is also indicated by the observed cytotoxic effects of linoleic and arachidonic acid.", 
"Hemophilia A is caused by the lack of functional blood-clotting factor VIII. We have used retrovirus-mediated gene transfer to generate various cell lines, rodent as well as human, that secrete the human factor VIII protein. To study whether transplantation of genetically modified fibroblasts is a feasible approach for gene therapy of hemophilia A, we implanted the factor VIII-secreting cells into immune-deficient mice. Implantation of factor VIII-secreting primary human skin fibroblasts resulted in long-term persistence of the transplanted cells; cells recovered from the implants up to 2 months post-implantation still had the capacity to secrete factor VIII when regrown in tissue culture. However, we were unable to detect any human factor VIII in plasma samples of the recipient mice. The absence of human factor VIII in the recipients' plasma is shown to be due neither to (epigenetic) inactivation of the retroviral vector in vivo, nor to inability of the stationary cells to secrete factor VIII protein. However, we did note a rapid clearing of the human factor VIII : CAg from plasma upon intravenous injection of plasma-derived human factor VIII in mice (t1/2 < 60 min vs. 10 hr in humans). This phenomenon can fully explain the apparent absence of human factor VIII in the recipients' plasma.", 
"The liver tumor-prone B6C3F1 mouse (C57BL/6female x C3H/Hemale), in conjunction with the more susceptible C3H/He paternal strain and the resistant C57BL/6 maternal strain, is an excellent model for studying the mechanisms involved in carcinogenesis. The study reported here indicated that the B6C3F1 mouse inherited a maternal raf allele containing a methylated site not present in the paternal allele. Seven days after partial hepatectomy or after administration of a promoting dose of phenobarbital (PB) for 14 d; raf in B6C3F1 mouse liver was hypomethylated. The additional methylated site in the allele inherited from C57BL/6 was not maintained. The methylation status of raf in the liver of the C57BL/6 mouse was not affected by PB treatment. This indicates that the B6C3F1 mouse is less capable of maintaining methylation of raf than the C57BL/6 strain is. In both PB-induced and spontaneous B6C3F1 liver tumors, raf was hypomethylated in a nonrandom fashion. The level of raf MRNA increased in seven of 10 PB-induced tumors but in only one of five spontaneous tumors, whereas the level of Ha-ras mRNA increased in nine of 10 PB-induced tumors and in four of five spontaneous tumors. The results of our investigation (a) support the hypothesis that hypomethylation of DNA is a nongenotoxic mechanism involved in tumorigenesis, (b) support the notion that PB promotes liver tumors that develop along a pathway different from that leading to spontaneous tumors, and (c) indicate that differences in DNA methylation between C57BL/6 and B6C3F1 mice could, in part, account for the unusually high tendency of the latter strain to develop liver tumors. (C) 1994 Wiley-Liss, Inc.", 
"Objective.-To evaluate the role of candidate genes in the susceptibility to multiple sclerosis (MS) and describe the role of T-cell receptor (TCR) gene rearrangements in the MS brain lesion in identifying a major target of the immune response in this disease. Data Sources.-MEDLINE, bibliography review of published data, and unpublished studies. Study Selection.-Published studies using novel molecular approaches to analyze the role of the major histocompatibility complex (MHC) and TCR gene complexes, as well as other candidate genes, in susceptibility to MS. We analyze epigenetic events involving TCR genes in individuals with MS and describe recent clinical trials in which immunotherapy has been attempted. Data Synthesis.-Consistent with a polygenic model for disease predisposition, MHC and TCR gene associations with MS are relatively weak. Despite intensive research, no other putative ''MS genes'' have been firmly established. The analysis of TCR rearrangements in the brain lesion has helped to identify a major target of the immune response in MS. Conclusion.-Understanding the genetic basis for autoimmune demyelination will offer new possibilities for the treatment of this illness.", 
"By analyzing a culture system of human prostatic epithelial cells (HPEC) and human prostatic fibroblasts (HPF) for expression of several determinants by immunocytochemistry, we have shown that long-term cultures are able to preserve the phenotypic characteristics of the normal tissue from which they are derived. The cytoskeletal elements, prostate-specific proteins, and steroid receptor profiles were compared to those of prostatic epithelium and stroma in situ. When cultured in low serum and low calcium medium, the adult HPEC grew as two layers of cells, the upper one of which retained the differentiation characteristics observed in the luminal fraction of normal prostatic epithelium. This cell type is the likely origin of prostatic neoplasia, with expression of CK8, 18, and 19 but not CK14. Androgen receptors, prostatic-specific antigen, and prostatic acid phosphatase are also expressed in vitro but at lower level than in situ. The lower cell layer expressed most of the same determinants but at a much lower level, suggestive of a stem-cell type. The HPF cultured in RPMI serum supplemented media retained the stromal pattern of the cells observed in situ. Culture systems which conserve the characteristics of their normal counterparts in vivo should provide useful models for studying in vitro genetic and epigenetic factors associated with differentiation and proliferation, but also with tumorigenic progression in the prostatic gland. (C) 1994 Academic Press, Inc.", 
"This study measured the effect of precise doses of 2-acetylaminofluorene (AAF) in inducing DNA damage, functional changes and neoplastic conversion in rat liver. Groups of male F344 rats at 9 weeks of age were exposed to cumulative doses of 0.5 or 2.0 mmol AAF per kg body weight given by gavage daily 5 days per week over an 8-week period and maintained with no further exposure for up to 8 weeks. Administration of AAF resulted in the formation of N-deoxyguanosin-(8-yl)-2-aminofluorene in liver DNA in relationship to dose. In centrilobular hepatocytes the zone of glutamine synthetase-expressing cells was reduced by exposure. By 8 weeks, but not at 4 weeks, the higher of the two doses of AAF provoked an increase in cell proliferation measured by immunohistochemical incorporation of bromode-oxyuridine. Altered hepatocellular foci expressing the placental form of glutathione transferase were induced by the high dose of AAF at 4 weeks, but not at the low dose. At 8 weeks the incidence of foci at the high dose was 79 times that induced by the low dose. These foci were highly proliferative. In animals exposed to AAF for 8 weeks and maintained for 4 weeks with no exposure, DNA adducts decreased by 80% and cell proliferation subsided by 80%, although the glutamine synthetase zone remained diminished. After discontinuation of AAF, the number of foci diminished by 50% and their proliferation subsided by 80% at 4 weeks, indicating a phenotypic reversion of many foci. With this protocol of administration of precise doses of AAF, we have established non-linearity of effects and a lack of correlation between DNA adduct formation and induction of cellular lesions. We suggest that doses in the range of those reported can be used to study the contribution of epigenetic and genotoxic effects in carcinogenesis and to study threshold events.", 
"The hepatocarcinogenicity of peroxisome proliferators (PPs) in rodents has been attributed both to oxidative DNA damage resulting from excessive leakage of peroxisomal H2O2 and to increased hepatocellular replication that may be independent of peroxisome proliferation. Because of the growing association between tumor promotion and alterations in growth-regulatory signal transduction pathways, we investigated whether PPs can modulate these pathways in a mouse liver epithelial cell line, BNL-CL.2. We tested two PPs that differ markedly in rodent tumorigenicity for their ability to activate immediate-early proto-oncogene expression. 4-Chloro-6-(2,3-xylidino)-2-pyrimidinylthioacetic acid (Wy-14643), a highly tumorigenic PP, was an exceptionally strong inducer of c-fos expression. In contrast, diethylhexyl phthalate (DEHP), a weakly tumorigenic PP, was a very poor inducer of c-fos expression. Wy-14643 was also stronger than DEHP in stimulating c-jun expression, whereas both PPs were fairly strong inducers of jun-B and jun-D. The induction of fos and jun expression by Wy-14643 was specifically inhibited by the protein kinase C inhibitor 1-(5-isoquinolinesulfonyl)-2-methylpiperizine dihydrochloride (H-7). DEHP-induced gene expression was strongly inhibited by H-7, but was also partially inhibited by an inhibitor of protein kinase A. The activation of fos and jun gene expression by PPs was independent of peroxisome proliferation since it was an immediately-early response not requiring protein synthesis and since the cell lines used in this study do not undergo peroxisome proliferation. Our results raise the possibility that the carcinogenicity of PPs may be due, in part, to epigenetic modulation of growth-regulatory signal transduction pathways. (C) 1993 Wiley-Liss, Inc.", 
"Supine arterial blood pressure measurements of 89 patients with homozygous sickle cell disease and normal renal function were compared with those of an age-, race-, and sex-matched normal population and with those of individuals who had similar levels of anemia due to beta thalassemia. Consistent with previous reports, sickle cell patients had significantly lower blood pressure than the normal population. However, within most age groups, sickle cell patients tended to have higher than expected blood pressure than individuals with similar or less severe degrees of anemia. Furthermore, the authors have found an association between cerebrovascular accident and elevated blood pressure in men, even in a range of systolic and diastolic pressures that would be considered normal by conventional standards. These results reiterate the intricate relationship that exists between factors governing red cell rheology and microvascular tone. They also raise the possibility that ''relative'' hypertension may be associated with other vaso-occlusive manifestations of the sickle cell syndromes.", 
"5-Azacytidine (5-aza-CR) and 5-aza-2'-deoxycytidine (5-aza-CdR), analogs of cytidine modified in position 5, were originally developed as antitumor agents, and have been useful in the treatment of both childhood and adult leukemias. These agents are cytotoxic per se, but also induce differentiation in several experimental systems, most notably the induction of muscle, adipocytes, and chondrocytes in cultures of drug-treated mouse embryo fibroblasts. The mechanisms underlying this drug-induced differentiation have been difficult to unravel, a fact which limits the rational design of differentiation therapy as a modulator of cancer using these agents. Induction of new developmental pathways in cultured cells involves stable, heritable changes, presumably of an epigenetic nature. Our early studies demonstrated that changes in methylation of cytosine in DNA occurred concurrently with changes in developmental potential, and that the presence of 5-azacytosine in DNA interfered with the action of DNA methyltransferase. Since DNA methylation is believed to be involved at some level in the regulation of gene expression, the hypothesis was developed that changes in methylation allowed the expression of new genes whose activity initiated new pathways of differentiation. The characterization of this drug-induced system of differentiation has therefore opened the way to identifying genes directly involved in the initiation or modification of pathways of differentiation. The first of these was MyoD, a member of a family of myogenic determination genes. Expression of MyoD in myogenic cell lines has been correlated with loss of methylation at specific sites in the genome, but the critical events leading to expression of MyoD and muscle differentiation are poorly understood. Recant developments in understanding this mechanism are discussed.", 
"The dose and time dependence of the cellular phenotype in preneoplastic and neoplastic liver lesions was evaluated quantitatively in groups of male Sprague-Dawley rats exposed for 7 weeks to 0, 12 and 24 mg/kg body wt of N-nitrosomorpholine (NNM) and studied at different time points up to 80 weeks after withdrawal of NNM (stop model). NNM-treated rats showed a dose- and time-dependent increase in the total number and volume of preneoplastic foci of altered hepatocytes (FAH) and in the incidence of hepatocellular adenomas (HCA) and carcinomas (HCC) at both dose levels, compared with the untreated controls. After stopping treatment with 12 mg/kg body wt, the well-known sequence of cellular changes leading from glycogenotic clear and clear/acidophilic cell foci to mixed and diffusely basophilic cell populations poor in glycogen was found. In contrast, at the higher NNM dose level (24 mg/kg) predominantly mixed and diffusely basophilic cell foci appeared immediately after cessation of treatment, but their number rapidly declined up to 13 weeks after withdrawal. At the same time, there was a reciprocal increase in the number of the less altered clear/acidophilic cell foci, indicating an early reversion-linked phenotypic instability of FAH. However, in spite of this reversion higher numbers of mixed and diffusely basophilic cell foci were retained after treatment with 24 compared to 12 mg/kg of NNM at all time points studied, and there was even a slow additional increase in the number of these types of FAH 20 weeks after withdrawal of NNM. At both dose levels, the volume fraction of the persistent mixed cell foci correlated positively with the incidence of HCA and HCC, suggesting that this phenotype of FAH represents a direct precursor of the neoplastic lesions. Tigroid cell foci, which appeared most frequently after treatment with the lo,ver dose of NNM, were not integrated into the predominant sequence of cellular changes leading to HCC, but they may represent an intermediate stage in a side lineage of this sequence, endowed with the potential to progress at least to HCA. Our results show that reversion-linked phenotypic instability of FAH occurs mainly after high dose treatment, possibly resulting from rapid adaptive cellular responses to the primary carcinogenic lesion(s) which may be fixed by genetic or epigenetic mechanisms. In contrast, progression-linked phenotypic instability of FAH is a slow process developing in a dose- and time-dependent manner at all dose levels leading to hepatic neoplasia.", 
"Carcinogenesis is a complex process characterized by the cumulative activation of various oncogenes and the inactivation of suppressor genes. Epigenetic mechanisms are also involved. Mutational activation of ras family genes occurs in most spontaneous or carcinogen-induced liver tumors, in susceptible mice, and less frequently in preneoplastic lesions. This suggests a pathogenetic role of these changes in hepatic carcinogenesis, in the mouse. Overexpression of various growth-related genes occurs in preneoplastic tissue during rat liver carcinogenesis, but mutational activation of protooncogenes, notably of ras family genes, seems to be a late and rare event, while c-myc amplification is a late but frequent event in both rodent and human carcinogenesis. However, mutation of the suppressor p53 gene has been found in relatively early preneoplastic lesions in rat liver, and it may be frequently seen in human hepatocellular carcinomas. The possibility that this mutation is involved in the initiation stage of liver carcinogenesis is an attractive hypothesis which needs further evaluation. DNA hypomethylation is involved in carcinogenesis, but the mechanisms underlying this effect are still elusive. Hypomethylation of growth-related genes is associated with their overexpression and this could favor overgrowth of preneoplastic liver tissue. Decrease in S-adenosyl methionine/S-adenosylhomocysteine (SAM/SAH) ratio occurs in the liver of rats fed a methyl deficient diet, which is a carcinogenic treatment, and in preneoplastic liver tissue, developing in initiated/promoted rats fed an adequate diet. The role of low SAM/SAH ratio in carcinogenesis is substantiated by the tumor chemopreventive effect of lipotropic compounds. Treatment with exogenous SAM prevents the development of preneoplastic and neoplastic lesions in rat liver. This is associated with recovery of SAM/SAH ratio, DNA methylation and inhibition of growth-related gene expression. SAM effect on prenoplastic cell growth is abolished by 5-azacytidine, a hypomethylating agent, indicating the involvement of DNA methylation. The possibility that in SAM-treated rats, methylation and inhibition of the expression of growth-related genes is implicated in growth restraint is attractive and should be further evaluated. Modulation of rat liver carcinogenesis by influencing gene expression through DNA methylation or other epigenetic mechanisms could be a new approach to chemoprevention of these tumors.", 
"Isolated limb perfusion with melphalan is a long-standing treatment for melanoma but the clinical conditions have not been subjected to a systematic evaluation. In order to establish optimal conditions for perfusion, three human melanoma cell lines were cultured with melphalan in vitro under conditions comparable to in vivo therapy. The most important findings were that: (a) 41.5-degrees-C was synergistic for melphalan killing of three human melanoma cell lines; (b) prolonging the treatment time beyond 1 h had little additional toxicity; and (c) varying the initial pH of the culture medium had no effect. After 1 h of treatment, cells accumulated more melphalan at 41.5-degrees-C than at 37-degrees-C, relative to the extracellular concentration. A cell line (MM418) derived from a primary tumour was the most resistant of the three lines; pigmented or non-pigmented sublines were equally resistant. The A2058 line showed the lowest level of synergism with hyperthermia, and displayed a marked plateau at 10% of controls in the dose-response for survival, yet no melphalan-resistant subpopulation could be isolated. The implications of this work are that (a) enhanced cellular uptake of melphalan may account for hyperthermic synergism of melphalan; (b) varying conditions other than treatment time will be necessary to deal with the variation in resistance between tumours; and (c) repeated cycles of treatment may be needed for phenotypes such as A2058 where melphalan resistance appears to be based on an epigenetic mechanism.", 
"Regulation of the expression of the DNA repair enzyme O6-methylguanine-DNA methyltransferase (MGMT) has been investigated in a number of human lymphoblastoid cell lines. In a number of Mex- cell lines that do not express methyltransferase activity, CpG sequences in the mgmt gene were hypomethylated with respect to methyltransferase-expressing Mex+ lines. In the cell line GM1953(S), in which the mgmt gene is coregulated with the thymidine kinase and galactokinase genes, reexpression of all three activities was experimentally induced. In this case, the mgmt gene in the nonexpressing cells was found to be hypermethylated and underwent a demethylation at CpG sequences that was coincident with the reappearence of the mgmt mRNA and the three enzyme activities. The simultaneous silencing of three activities in these cells was correlated with an increase in DNA 5-methylcytosine that was widespread thoughout the genome. The data indicate that MGMT expression can be controlled epigenetically in human lymphoid cell lines, although the relationship between cytosine methylation and MGMT expression is complex. Furthermore, the rapid alterations in methylation in GM1953(S) cells indicate the existence of signals that can induce widespread and abrupt alterations in cytosine methylation in human cells in culture.", 
"Long-term culturing of viral Kirsten-ras-oncogene (v-Ki-ras)-transformed BALB/c 3T3 cells (KiMSV) selectively enriches for cells which have deleted the viral oncogene. In contrast, v-Ki-ras in vivo is amplified and expression increased in all late-stage tumors and lung metastases relative to late-passage KiMSV cells being injected. The nature and significance of these selection processes, in terms of the v-Ki-ras gene, have been explored using genetically-tagged cells, as have the properties of v-Ki-ras- revertant subclones. Inoculation of KiMSV late-passage cells (containing < 5% v-Ki-ras+ cells) into nude mice, generated primary and lung metastatic tumors with the v-Ki-ras gene at increased dosage in all tumors and their single-cell clones, isolated at both early and late stages of tumor developments; this demonstrates early and specific in vivo selection for v-Ki-ras+ cells in both induction and progression of tumors in this system. v-Ki-ras- revertant subclones, isolated from the late-passage KiMSV cells and inoculated individually into athymic nude mice, yielded tumors for only 1 of the 4 revertants, with no evidence for v-Ki-ras sequences in these tumor cells, thereby revealing a v-Ki-ras-independent mechanism for tumor formation in a small subset of revertant cells. Mixtures of the 4 subclones yielded tumors in all animals, although at a much longer latent period than observed with v-Ki-ras+ cells. Experiments with mixtures of v-Ki-ras- revertant cells and pSV2neotagged/v-Ki-ras+ cells (both complex Neo(R) cell mixtures and individual Neo(R) clones tested) at various cell ratios revealed clonal variability among v-Ki-ras+ cells for dominance during tumor formation. Moreover, the complex Neo(R) cell mixtures yielded both primary and metastatic tumors with simplified patterns of pSV2neo integration sites, suggesting that secondary genetic or epigenetic events, in addition to v-Ki-ras, contribute to the tumor-progressing phenotype. These experiments taken together demonstrate (a) clone-specific early selection of distinct v-Ki-ras+ cells amongst themselves and over v-Ki-ras- cells in both induction and progression of tumors, (b) reduced tumorigenic competence of v-Ki-ras- revertant cells, with a small subset displaying a v-Ki-ras-independent mechanism for tumor formation in this BALB/c 3T3 system, and (c) the significance of additional genetic or epigenetic events for tumor-progressing competence in unique subsets of v-Ki-ras+ cells.", 
"Emerging evidence suggests that breast cancer may originate during early life. In particular, offspring of mothers who during pregnancy exhibited behaviors that are associated with increased incidence of breast cancer, may be at risk. These behaviors include intake of high fat diet or alcohol, or stressful life style. We have found that neonatal exposure to handling that leads to improved ability to cope with stress, reduces 7,12-dimethylbenz(a)anthracene (DMBA)-induced mammary tumors in rats. Further, our results indicate that maternal exposure to high fat diet increases the incidence of DMBA-induced mammary tumors in female offspring. High fat diet also increases serum 17 beta-estradiol (E2) levels in pregnant animals. These results support the hypothesis that in utero concentrations of estrogens play a critical role in the vulnerability to develop boast cancer. The mechanism of estrogen action might be related to its effect on the induction of epithelial hyperplasia and altered breast differentiation. These events then increase the rate of genetic/epigenetic changes that increase the possibility of neoplastic transformation. Increased pregnancy estrogens may also lead to behavioral alterations in the offspring. This could explain the proposed association between certain behavioral patterns and increased tumorigenity. Our results in transgenic mice overexpressing transforming growth factor alpha (TGF alpha) are in accordance with this interpretation. The male TGF alpha mice exhibit elevated serum E2 levels, impaired ability to cope with stress, increased voluntary alcohol intake and high incidence of spontaneous hepatocellular tumors. These findings indicate that animal models offer a unique opportunity to investigate the role of timing of risk behaviors on breast cancer. They are also useful in the attempts to understand the mechanism of early estrogen action on mammary tumorigenesis.", 
"Metastasis is a complex non-stochastic process that is most likely the result of genetic and epigenetic interactions of a wide variety of genes. The search for a single gene which can encompass such a pleiotropic response as to account for the observed phenotypic characteristics of metastatic tumour populations has been unsuccessful. Particular studies involving gene transfection, subtractive hybridisation and cell fusion are beginning to identify specific genes which contribute to metastasis in some cell types. However, such analyses are complicated by the inherent genetic instability and phenotypic heterogeneity present in tumour populations. A more detailed understanding of the metastatic process may require an abandoning of current generalised approaches to metastasis in favour of concentrating on key components of the metastatic cascade such as adhesion and invasion.", 
"Models of animal melanoma are still indispensable tools in oncological research because they can be studied in syngeneic hosts while human melanomas cannot. One such model is a family of melanomas which originated in 1959 from a spontaneous melanotic melanoma of the skin in Syrian hamster, the Bomirski melanomas. Currently, it consists of 5 transplantable in vivo-variants (Ma, Ab, MI, MI-B and Ab455) and several cell lines derived from Ab amelanotic and Ma melanotic tumors. Here we present the Bomirski family of melanomas as an excellent model to study regulatory mechanisms governing melanogenesis, differentiation and intermediary metabolism in melanocytes, and as a good animal model for developing and testing potential melanoma vaccines.", 
"Genomic imprinting results in a functional non-equivalence of parental chromosomes, presumably by epigenetic modification of the genome, and is required for normal mammalian development. In general, reciprocal phenotypes are observed in embryos containing alterations in the dosage of parental chromosomes, for example where both copies of chromosomes or chromosomal regions are derived from one parent. These phenotypes indicate that duplications of maternal chromosomes inhibit embryonic growth and proliferation whereas duplications of the paternal genome result in enhanced cell growth and proliferation. Alterations in the dosage of parental chromosomes have recently been observed in some forms of recessive tumour in man. Here we discuss the role and possible mechanisms of genomic imprinting during embryogenesis and attempt to draw parallels between the parental origin of the loss of heterozygosity observed in some human tumours and the developmental phenotypes that arise in mice with similar distortions of parental origin. These observations strongly implicate genomic imprinting in the genesis of some forms of tumour and, more generally, in the genetic predisposition to cancer.", 
"The prevention of cancer is, at our present state of knowledge, the most effective and inexpensive mode of controlling this disease. Passive cancer prevention is practiced voluntarily or, in part, through governmental regulation in many parts of the world. However, active cancer prevention by the administration of vaccines, dietary factors, antihormones, or other agents is likely to be the most effective mechanism of cancer prevention in humans. Carcinogenesis develops in three defined stages-initiation, promotion, and progression-the first and third resulting from irreversible genetic changes in the cell, whereas the intermediate stage of promotion involves an epigenetic alteration of the expression of the genome and cell division. Thus, the stage of promotion is the most effective site to target for both active and passive cancer prevention. A review of the modalities presently used in cancer prevention, both active and passive, demonstrates that all such methods involve an inhibition and/or reversal of this intermediate stage, thus preventing the development of the malignant process. Future advances in cancer prevention will depend on better knowledge of the mechanisms of the stages of carcinogenesis in order that rational preventive agents and formats may be used in altering or modifying the appropriate stage(s) of neoplastic development.", 
"Tumor progression is a multistep process involving genetic and epigenetic changes in a transformed clone. Some of these changes may be induced by host factors which may also select for transformed cellular variants with a high ability to survive and propagate. In this article we review studies showing that receptors for the Fc portion of IgG may be expressed on cells from human or animal tumors of nonlymphoid origin. We also review data demonstrating that at least with respect to cells transformed in vitro with Polyoma virus, transformation per se is not sufficient for the induction of Fc receptor expression. We also summarize preliminary data showing that Fc receptor expression is causally involved in conferring a high malignancy phenotype upon transformed cells. Possible mechanisms to explain these observations are discussed.", 
"Epigenetic changes may play a role in genetic alterations in cancer cells, but little is known about this phenomenon. In this study we examined the correlation between rearrangement and methylation status of the T-cell receptor (TCR) beta-chain gene in 23 patients with B precursor acute lymphoblastic leukemia (ALL). In B precursor ALL, all patients had a CC(me) GG sequence in the C-beta-2 region, a pattern similar to that observed in normal mature B-cells. Approximately 55% of patients with B precursor ALL exhibiting a hypomethylated CCGG sequence at the J-beta-1 region showed rearrangement of this region. Furthermore, the same allele of rearranged J-beta-1 always contained an unmethylated sequence in the region, although another allele without rearrangement contained methylated J-beta-1. By contrast, none of the patients had a rearrangement in the J-beta-1 region without hypomethylation. Therefore, rearrangement of the J-beta-1 region may link to the hypomethylation status of this region. A close association between hypomethylation and rearrangement of the TCR-beta-chain gene indicates that hypomethylation of the J-beta-1 region may promote accessibility to a putative common recombinase to produce TCR J-beta-1 rearrangement. In contrast, about 45% of patients with a hypomethylated J-beta-1 did not show rearrangement in this region, thus allowing categorization of B precursor ALL patients into subtypes, according to the combination of TCR-beta-chain gene rearrangement and hypomethylation status, especially in the J-beta-1 region.", 
"The thiopurines 6-thioguanine (6TG) and 6-mercaptopurine (6MP) are cytotoxic to proliferating cells by a mechanism involving incorporation into DNA via the purine salvage pathway, and resistance to these agents can be conferred by lack of the salvage pathway enzyme hypoxanthine-guanine phosphoribosyltransferase. However, human and murine hypoxanthine-guanine phosphoribosyltransferase-deficient leukemia cell Lines have been shown to respond to 6TG by growth arrest and differentiation by a mechanism apparently not involving incorporation of 6TG into DNA. If so, leukemia cells resistant to 6MP should still respond to 6TG by growth arrest via an undescribed epigenetic mechanism. To test this, polyclonal 6MP-resistant variants were produced from three human leukemia cell lines, HL-60, U937, and CCRF-CEM. Treatment of both sensitive and resistant cells with 6TG induced growth arrest. The effect of 6TG in the 6MP-sensitive HL-60 and U937 cells was associated with significant loss of viability and DNA fragmentation. In contrast, the 6TG-treated 6MP-resistant cells exhibited a slower decline in viability and no DNA fragmentation. To identify the mechanism by which 6TG may induce growth arrest, tRNA was isolated from 6MP-resistant cells cultured for 48 h with 6TG. 6TG was found to be incorporated into tRNAs normally containing queuine in the anticodon wobble position. These studies may provide a basis for the development of new therapeutic regimens for the treatment of leukemia.", 
"Rapid progress in understanding the biology of colorectal carcinoma has occurred in the last decade. During this time, the importance of tumor suppressor genes has been delineated. Mutations in proto-oncogenes, and some of the genetic and epigenetic defects that occur during neoplastic transformation, have been characterized. The very recent identification of a technology that detects some mutations in genes by analyzing fecal specimens offers the real prospect of effective, low-cost screening of large segments of the population at risk for the development of large bowel cancer. A better understanding of the mechanisms involved in metastasis is slowly leading to better methods of prognostication for patients with carcinoma of the colon or rectum. This is important because a better biologic identification of patients at high risk for subsequent metastasis will help determine which patients should receive adjuvant therapy. Further, the development of new approaches to inhibit various aspects of the cascade of events necessary to produce metastasis, notably die inhibition of neovascularization, suggests the real possibility that established metastases may be treated by relatively nontoxic medical therapies. As a result, further knowledge of the biology of colorectal cancer will translate into strategies that will continue to improve the control of this prevalent carcinoma.", 
"The epigenetic phenomenon could play a role in the interaction between chromatin and DNA-binding enzymes, allowing us to consider an association between the phenomenon and gene rearrangement. The correlation between methylation status and rearrangement of the T-cell receptor (TCR) beta chain gene in leukemia cells obtained from patients with acute myeloid leukemia (AML) was examined. All of the AML patients with a TCR-beta rearrangement had hypomethylated CCGG sequences within the Jbeta1 region on the rearranged allele, while the germ-line allele had completely methylated CC(me)GG sequence in this region, indicating a strong association between hypomethylation status and rearrangement of the TCR beta chain gene. In the DNA from AML patients with or without a TCR-beta rearrangement, the Cbeta2 region contained completely methylated CC(me)GG sequences, even though they express T-cell-associated antigens, including CD7; this pattern is quite different from that observed in T-cell neoplasias. Moreover, some AML patients showed a TCR-beta rearrangement without the presence of immunoglobulin heavy-chain gene rearrangement, suggesting that TCR beta chain gene involvement in AML is required for unknown factors other than common recombinase activity.", 
"Analyses to detect loss of heterozygosity (LOH) were performed at 11 polymorphic loci on chromosome 11 and, using a polymorphic CA repeat sequence in the WT1 gene, on a series of 39 tumours from 28 unilateral and 10 tumours from 6 bilateral Wilms' tumour (WT) patients. LOH was seen in 13 out of 35 patients including 12 out of 29 unilateral tumours, but only one of 10 bilateral tumours. This suggests that bilateral WT represents a subgroup of WT in which tumour initiating events less frequently involve LOH on chromosome 11 and that either epigenetic events, point mutations or another non-chromosome 11p locus are important in bilateral tumours. The observation of LOH in one WT but not another WT in a bilateral WT patient provides evidence that these tumours arising in the same patient are not monoclonal proliferations and most likely arise via different molecular pathways.", 
"Loss of cell-substratum adhesion is an important factor during tumour progression. We have previously described reduced focal contact components and poorly organized cytoskeletal actin in renal cell carcinomas. In this study, we have used the potent tumour promoter TPA on cultured human renal epithelium to mimic neoplastic transformation. The morphological changes induced by TPA were examined by phase contrast and fluorescence microscopy. TPA treatment caused rounding up of cells and loss of adhesion to either fibronectin or laminin substrata. Cytoskeletal actin was redistributed from orientated stress fibre bundles to a perinuclear circumferential arrangement. This was accompanied by a progressive reduction in the number of vinculin-containing contacts with accumulation of vinculin in punctate spots in the perinuclear region. These altered membrane-cytoskeletal interactions induced by TPA are entirely reversible and mimic epigenetic changes which occur during tumour progression.", 
" ", 
"The Philadelphia (Ph) translocation [t(9;22)(q34;q11)] is the most common genetic abnormality in human leukemia; a transposition of the ABL gene to the major-breakpoint cluster region (M-BCR) is associated with the pathogenesis in Ph+ chronic myelogenous leukemia (Ph+ CML) and in some cases of Ph+ acute leukemia (Ph+ AL). Our current understanding of the methylation of human genomes allows us to consider the association between the epigenetic phenomenon and the control of differentiation and proliferation in mammalian cells. In order to determine whether the methylation status of the M-BCR is associated with breakpoint-localization in this region and with the lineage of hematopoietic cells, we have examined 28 patients with Ph+ leukemias, including nine with Ph+ AL, six patients with acute myeloblastic leukemia without Ph (Ph- AML), and five patients with Ph- acute lymphoblastic leukemia (Ph- ALL); using the restriction endonuclease isochizomers, MspI and HpaII. In CML patients in the chronic phase, the hypomethylated status within the normal M-BCR allele is heterogeneous. In contrast, patients with Ph- CML in the lymphoid blast crisis phase exhibited a 2.5/2.7 kb band with a complete disappearance of the germline M-BCR fragment (type L). This pattern is consistently noted in Ph- ALL cells, and the pattern is quite different from that found in myeloid blast crisis or Ph- AML (type M). In patients with M-BCR-nonrearranged Ph+ ALL, it is suggested that the M-BCR methylation patterns are cell-lineage specific but some Ph+ ALL cells had a hypomethylation pattern thal was identical to that observed in Ph- AML, suggesting a distinction of genetic diversity of leukemia cells with the Ph chromosome, especially Ph+ AL.", 
"We karyotyped two histologically distinct components with different metastatic behavior of a testicular nonseminomatous germ cell tumor. The two components showed an almost identical chromosomal pattern. These almost identical karyotypes of the two components with different metastatic potential suggest that the difference in biologic behavior might result from subtle differences (on microscopic or submicroscopic level) in chromosomal pattern or that these differences are predominantly epigenetically determined and depend primarily on the lineage of differentiation of the tumor component. Trophoblastic differentiation results in an aggressive, angioinvasive tumor but in development of teratoma in a tumor with low malignant potential.", 
" ", 
" ", 

"Individual animals frequently exhibit repeatable differences from other members of their population, differences now commonly referred to as 'animal personality'. Personality differences can arise, for example, from differences in permanent environmental effects-including parental and epigenetic contributors- and the effect of additive genetic variation. Although several studies have evaluated the heritability of behaviour, less is known about general patterns of heritability and additive genetic variation in animal personality. As overall variation in behaviour includes both the among-individual differences that reflect different personalities and temporary environmental effects, it is possible for personality to be largely genetically influenced even when heritability of behaviour per se is quite low. The relative contribution of additive genetic variation to personality variation can be estimated whenever both repeatability and heritability are estimated for the same data. Using published estimates to address this issue, we found that approximately 52% of animal personality variation was attributable to additive genetic variation. Thus, while the heritability of behaviour is often moderate or low, the heritability of personality is much higher. Our results therefore (i) demonstrate that genetic differences are likely to be a major contributor to variation in animal personality and (ii) support the phenotypic gambit: that evolutionary inferences drawn from repeatability estimates may often be justified.", 
"Environment has a critical role in the natural selection process for Darwinian evolution. The primary molecular component currently considered for neo-Darwinian evolution involves genetic alterations and random mutations that generate the phenotypic variation required for natural selection to act. The vast majority of environmental factors cannot directly alter DNA sequence. Epigenetic mechanisms directly regulate genetic processes and can be dramatically altered by environmental factors. Therefore, environmental epigenetics provides a molecular mechanism to directly alter phenotypic variation generationally. Lamarck proposed in 1802 the concept that environment can directly alter phenotype in a heritable manner. Environmental epigenetics and epigenetic transgenerational inheritance provide molecular mechanisms for this process. Therefore, environment can on a molecular level influence the phenotypic variation directly. The ability of environmental epigenetics to alter phenotypic and genotypic variation directly can significantly impact natural selection. Neo-Lamarckian concept can facilitate neo-Darwinian evolution. A unified theory of evolution is presented to describe the integration of environmental epigenetic and genetic aspects of evolution.", 
"DNA methylation contributes to gene and transcriptional regulation in eukaryotes, and therefore has been hypothesized to facilitate the evolution of plastic traits such as sociality in insects. However, DNA methylation is sparsely studied in insects. Therefore, we documented patterns of DNA methylation across a wide diversity of insects. We predicted that underlying enzymatic machinery is concordant with patterns of DNA methylation. Finally, given the suggestion that DNA methylation facilitated social evolution in Hymenoptera, we tested the hypothesis that the DNA methylation system will be associated with presence/absence of sociality among other insect orders. We found DNA methylation to be widespread, detected in all orders examined except Diptera (flies). Whole genome bisulfite sequencing showed that orders differed in levels of DNA methylation. Hymenopteran (ants, bees, wasps and sawflies) had some of the lowest levels, including several potential losses. Blattodea (cockroaches and termites) show all possible patterns, including a potential loss of DNA methylation in a eusocial species whereas solitary species had the highest levels. Species with DNA methylation do not always possess the typical enzymatic machinery. We identified a gene duplication event in the maintenance DNA methyltransferase 1 (DNMT1) that is shared by some Hymenoptera, and paralogs have experienced divergent, nonneutral evolution. This diversity and nonneutral evolution of underlying machinery suggests alternative DNA methylation pathways may exist. Phylogenetically corrected comparisons revealed no evidence that supports evolutionary association between sociality and DNA methylation. Future functional studies will be required to advance our understanding of DNA methylation in insects.", 
" ", 
"Phenotypic characteristics of animals can change independently from changes in the genetic code. These plastic phenotypic responses are important for population persistence in changing environments. Plasticity can be induced during early development, with persistent effects on adult phenotypes, and it can occur reversibly throughout life (acclimation). These manifestations of plasticity have been viewed as separate processes. Here we argue that developmental conditions not only change mean trait values but also modify the capacity for acclimation. Acclimation counteracts the potentially negative effects of phenotype-environment mismatches resulting from epigenetic modifications during early development. Developmental plasticity is therefore also beneficial when environmental conditions change within generations. Hence, the evolution of reversible acclimation can no longer be viewed as independent from developmental processes.", 
"An organism's phenotype can be influenced by maternal cues and directly perceived environmental cues, as well as by its genotype at polymorphic loci, which can be interpreted as a genetic cue. In fluctuating environments, natural selection favors organisms that efficiently integrate different sources of information about the likely success of phenotypic alternatives. In such situations, it can be beneficial to pass on maternal cues that offspring can respond to. A maternal cue could be based on environmental cues directly perceived by the mother but also partly on cues that were passed on by the grandmother. We have used a mathematical model to investigate how the passing of maternal cues and the integration of different sources of information evolve in response to qualitatively different kinds of temporal and spatial environmental fluctuations. The model shows that the passing of maternal cues and the transgenerational integration of sources of information readily evolve. Factors such as the degree of temporal autocorrelation, the predictive accuracy of different environmental cues, and the level of gene flow strongly influence the expression of adaptive maternal cues and the relative weights given to different sources of information. We outline the main features of the relation between the characteristics of environmental fluctuations and the adaptive systems of phenotype determination and compare these predictions with empirical studies on cue integration.", 
"Understanding how organisms cope with global change is a major scientific challenge. The molecular pathways underlying rapid adaptive phenotypic responses to global change remain poorly understood. Here, we highlight the relevance of two environment-sensitive molecular elements: transposable elements (TEs) and epigenetic components (ECs). We first outline the sensitivity of these elements to global change stressors and review how they interact with each other. We then propose an integrative molecular engine coupling TEs and ECs and allowing organisms to fine-tune phenotypes in a real-time fashion, adjust the production of phenotypic and genetic variation, and produce heritable phenotypes with different levels of transmission fidelity. We finally discuss the implications of this molecular engine in the context of global change.", 
"Existing insight suggests that maternal effects have a substantial impact on evolution, yet these predictions assume that maternal effects themselves are evolutionarily constant. Hence, it is poorly understood how natural selection shapes maternal effects in different ecological circumstances. To overcome this, the current study derives an evolutionary model of maternal effects in a quantitative genetics context. In constant environments, we show that maternal effects evolve to slight negative values that result in a reduction of the phenotypic variance (canalization). By contrast, in populations experiencing abrupt change, maternal effects transiently evolve to positive values for many generations, facilitating the transmission of beneficial maternal phenotypes to offspring. In periodically fluctuating environments, maternal effects evolve according to the autocorrelation between maternal and offspring environments, favoring positive maternal effects when change is slow, and negative maternal effects when change is rapid. Generally, the strongest maternal effects occur for traits that experience very strong selection and for which plasticity is severely constrained. By contrast, for traits experiencing weak selection, phenotypic plasticity enhances the evolutionary scope of maternal effects, although maternal effects attain much smaller values throughout. As weak selection is common, finding substantial maternal influences on offspring phenotypes may be more challenging than anticipated.", 
"As climate change challenges organismal fitness by creating a phenotype-environment mismatch, phenotypic plasticity generated by epigenetic mechanisms (e.g., DNA methylation) can provide a temporal buffer for genetic adaptation. Epigenetic mechanisms may be crucial for sessile benthic marine organisms, such as reef-building corals, where ocean acidification (OA) and warming reflect in strong negative responses. We tested the potential for scleractinian corals to exhibit phenotypic plasticity associated with a change in DNA methylation in response to OA. Clonal coral fragments of the environmentally sensitive Pocillopora damicornis and more environmentally robust Montipora capitata were exposed to fluctuating ambient pH (7.9-7.65) and low pH (7.6-7.35) conditions in common garden tanks for similar to 6 weeks. M. capitata responded weakly, or acclimated more quickly, to OA, with no difference in calcification, minimal separation of metabolomic profiles, and no change in DNA methylation between treatments. Conversely, P. damicornis exhibited diminished calcification at low pH, stronger separation in metabolomic profiles, and responsiveness of DNA methylation to treatment. Our data suggest corals differ in their temporal dynamics and sensitivity for environmentally triggered real-time epigenetic reprogramming. The generation of potentially heritable plasticity via environmental induction of DNA methylation provides an avenue for assisted evolution applications in corals under rapid climate change.", 
"Migration is essential for the reproduction and survival of many animals, yet little is understood about its underlying molecular mechanisms. We used the salmonid Oncorhynchus mykiss to gain mechanistic insight into smoltification, which is a morphological, physiological and behavioural transition undertaken by juveniles in preparation for seaward migration. O. mykiss is experimentally tractable and displays intra- and interpopulation variation in migration propensity. Migratory individuals can produce nonmigratory progeny and vice versa, indicating a high degree of phenotypic plasticity. One potential way that phenotypic plasticity might be linked to variation in migration-related life history tactics is through epigenetic regulation of gene expression. To explore this, we quantitatively measured genome-scale DNA methylation in fin tissue using reduced representation bisulphite sequencing of F-2 siblings produced from a cross between steelhead (migratory) and rainbow trout (nonmigratory) lines. We identified 57 differentially methylated regions (DMRs) between smolt and resident O. mykiss juveniles. DMRs were high in magnitude, with up to 62% differential methylation between life history types, and over half of the gene-associated DMRs were in transcriptional regulatory regions. Many of the DMRs encode proteins with activity relevant to migration-related transitions (e.g. circadian rhythm pathway, nervous system development, protein kinase activity). This study provides the first evidence of a relationship between epigenetic variation and life history divergence associated with migration-related traits in any species.", 
"While traits and trait plasticity are partly genetically based, investigating epigenetic mechanisms may provide more nuanced understanding of the mechanisms underlying response to environment. Using AFLP and methylation-sensitive AFLP, we tested the hypothesis that differentiation to habitats along natural salt marsh environmental gradients occurs at epigenetic, but not genetic loci in two salt marsh perennials. We detected significant genetic and epigenetic structure among populations and among subpopulations, but we found multilocus patterns of differentiation to habitat type only in epigenetic variation for both species. In addition, more epigenetic than genetic loci were correlated with habitat in both species. When we analysed genetic and epigenetic variation simultaneously with partial Mantel, we found no correlation between genetic variation and habitat and a significant correlation between epigenetic variation and habitat in Spartina alterniflora. In Borrichia frutescens, we found significant correlations between epigenetic and/or genetic variation and habitat in four of five populations when populations were analysed individually, but there was no significant correlation between genetic or epigenetic variation and habitat when analysed jointly across the five populations. These analyses suggest that epigenetic mechanisms are involved in the response to salt marsh habitats, but also that the relationships among genetic and epigenetic variation and habitat vary by species. Site-specific conditions may also cloud our ability to detect response in replicate populations with similar environmental gradients. Future studies analysing sequence data and the correlation between genetic variation and DNA methylation will be powerful to identify the contributions of genetic and epigenetic response to environmental gradients.", 
"Epigenetic variation is being integrated into our understanding of adaptation, yet we lack models on how epigenetic mutations affect evolution that includes de novo genetic change. We model the effects of epigenetic mutations on the dynamics and endpoints of adaptive walks-a process where a series of beneficial mutations move a population towards a fitness optimum. We use an individual-based model of an asexual population, where mutational effects are drawn from Fisher's geometric model. We find cases where epigenetic mutations speed adaptation or result in populations with higher fitness. However, we also find cases where they slow adaptation or result in populations with lower fitness. The effect of epigenetic mutations on adaptive walks depends crucially on their stability and fitness effects relative to genetic mutations, with small-effect epigenetic mutations generally speeding adaptation, and epigenetic mutations with the same fitness effects as genetic mutations slowing adaptation. Our work reveals a complex relationship between epigenetic mutations and natural selection and highlights the need for empirical data.", 
"Environmental stresses experienced by individual parents can influence offspring phenotypes in ways that enhance survival under similar conditions. Although such adaptive transgenerational plasticity is well documented, its transmission mechanisms are generally unknown. One possible mechanism is environmentally induced DNA methylation changes. We tested this hypothesis in the annual plant Polygonum persicaria, a species known to express adaptive transgenerational plasticity in response to parental drought stress. Replicate plants of 12 genetic lines (sampled from natural populations) were grown in dry versus moist soil. Their offspring were exposed to the demethylating agent zebularine or to control conditions during germination and then grown in dry soil. Under control germination conditions, the offspring of drought-stressed parents grew longer root systems and attained greater biomass compared with offspring of well-watered parents of the same genetic lines. Demethylation removed these adaptive developmental effects of parental drought, but did not significantly alter phenotypic expression in offspring of well-watered parents. The effect of demethylation on the expression of the parental drought effect varied among genetic lines. Differential seed provisioning did not contribute to the effect of parental drought on offspring phenotypes. These results demonstrate that DNA methylation can mediate adaptive, genotype-specific effects of parental stress on offspring phenotypes.", 
"The role of natural selection in the evolution of adaptive phenotypes has undergone constant probing by evolutionary biologists, employing both theoretical and empirical approaches. As Darwin noted, natural selection can act together with other processes, including random changes in the frequencies of phenotypic differences that are not under strong selection, and changes in the environment, which may reflect evolutionary changes in the organisms themselves. As understanding of genetics developed after 1900, the new genetic discoveries were incorporated into evolutionary biology. The resulting general principles were summarized by Julian Huxley in his 1942 book Evolution: the modern synthesis. Here, we examine how recent advances in genetics, developmental biology and molecular biology, including epigenetics, relate to today's understanding of the evolution of adaptations. We illustrate how careful genetic studies have repeatedly shown that apparently puzzling results in a wide diversity of organisms involve processes that are consistent with neo-Darwinism. They do not support important roles in adaptation for processes such as directed mutation or the inheritance of acquired characters, and therefore no radical revision of our understanding of the mechanism of adaptive evolution is needed.", 
"The process of biological invasion exposes a species to novel pressures, in terms of both the environments it encounters and the evolutionary consequences of range expansion. Several invaders have been shown to exhibit rapid evolutionary changes in response to those pressures, thus providing robust opportunities to clarify the processes at work during rapid phenotypic transitions. The accelerating pace of invasion of cane toads (Rhinella marina) in tropical Australia during its 80-year history has been well characterized at the phenotypic level, including common-garden experiments that demonstrate heritability of several dispersal-relevant traits. Individuals from the invasion front (and their progeny) show distinctive changes in morphology, physiology and behaviour that, in combination, result in far more rapid dispersal than is true of conspecifics from long-colonized areas. The extensive body of work on cane toad ecology enables us to place into context studies of the genetic basis of these traits. Our analyses of differential gene expression from toads from both ends of this invasion-history transect reveal substantial upregulation of many genes, notably those involved in metabolism and cellular repair. Clearly, then, the dramatically rapid phenotypic evolution of cane toads in Australia has been accompanied by substantial shifts in gene expression, suggesting that this system is well suited to investigating the genetic underpinnings of invasiveness.", 
"DNA methylation in plants affects transposon silencing, transcriptional regulation and thus phenotypic variation. One unanswered question is whether DNA methylation could be involved in local adaptation of plant populations to their environments. If methylation alters phenotypes to improve plant response to the environment, then methylation sites or the genes that affect them could be a target of natural selection. Using reduced-representation bisulphite sequencing (RRBS) data, we assessed whether climate is associated with variation in DNA methylation levels among 58 naturally occurring, and species-wide samples of valley oak (Quercus lobata) collected across climate gradients. We identified the genomic context of these variants referencing a new draft valley oak genome sequence. Methylation data were obtained for 341 107 cytosines, of which we deemed 57 488 as single-methylation variants (SMVs), found in the CG, CHG and CHH sequence contexts. Environmental association analyses revealed 43 specific SMVs that are significantly associated with any of four climate variables, the majority of which are associated with mean maximum temperature. The 43 climate-associated SMVs tend to occur in or near genes, several of which have known involvement in plant response to environment. Multivariate analyses show that climate and spatial variables explain more overall variance in CG-SMVs among individuals than in SNPs, CHG-SMVs or CHH-SMVs. Together, these results from natural oak populations provide initial evidence for a role of CG methylation in locally adaptive evolution or plasticity in plant response.", 
"Comparative genomics of social insects has been intensely pursued in recent years with the goal of providing insights into the evolution of social behaviour and its underlying genomic and epigenomic basis. However, the comparative approach has been hampered by a paucity of data on some of the most informative social forms (e.g. incipiently and primitively social) and taxa (especially members of the wasp family Vespidae) for studying social evolution. Here, we provide a draft genome of the primitively eusocial model insect Polistes dominula, accompanied by analysis of caste-related transcriptome and methylome sequence data for adult queens and workers. Polistes dominula possesses a fairly typical hymenopteran genome, but shows very low genomewide GC content and some evidence of reduced genome size. We found numerous caste-related differences in gene expression, with evidence that both conserved and novel genes are related to caste differences. Most strikingly, these -omics data reveal a major reduction in one of the major epigenetic mechanisms that has been previously suggested to be important for caste differences in social insects: DNA methylation. Along with a conspicuous loss of a key gene associated with environmentally responsive DNA methylation (the de novo DNA methyltransferase Dnmt3), these wasps have greatly reduced genomewide methylation to almost zero. In addition to providing a valuable resource for comparative analysis of social insect evolution, our integrative -omics data for this important behavioural and evolutionary model system call into question the general importance of DNA methylation in caste differences and evolution in social insects.", 
"Epidemiological research since the 1980s has highlighted the consequences of early life adversity, particularly during gestation and early infancy, for adult health (the Barker hypothesis). The fast-evolving field of molecular epigenetics is providing explanatory mechanisms concerning phenotypic plasticity in response to developmental stressors and the accumulation of disease risk throughout life. In addition, there is now evidence for the heritability of poor health across generations via epigenetic modifications. This research has the potential to invoke a paradigmatic shift in how we interpret factors such as growth insults and immune response in past skeletal remains. It demonstrates that health cannot be understood in terms of immediate environmental circumstances alone. Furthermore, it requires both a theoretical and practical re-evaluation of disease biographies and the life course more generally. Individual life courses can no longer be regarded as discrete, bounded, life histories, with clearly defined beginning and end points. If socioeconomic circumstances can have intergenerational effects, including disease susceptibility and growth stunting, then individual biographies should be viewed as nested or embedded within the lives of others. This commingling of life courses may prove problematic to unravel; nevertheless, this review aims to consider the potential consequences for bioarchaeological interpretations. These include a greater consideration of: the temporal power of human skeletons and a life course approach to past health; infant health and the implications for maternal well-being; and the impact of non-proximate stressors (e.g., early life and ancestral environments) on the presence of health indicators. (C) 2015 Wiley Periodicals, Inc.", 
"Organisms develop through multiple life stages that differ in environmental tolerances. The seasonal timing, or phenology, of life-stage transitions determines the environmental conditions to which each life stage is exposed and the length of time required to complete a generation. Both environmental and genetic factors contribute to phenological variation, yet predicting their combined effect on life cycles across a geographic range remains a challenge. We linked submodels of the plasticity of individual life stages to create an integrated model that predicts life-cycle phenology in complex environments. We parameterized the model for Arabidopsis thaliana and simulated life cycles in four locations. We compared multiple genotypes by varying two parameters associated with natural genetic variation in phenology: seed dormancy and floral repression. The model predicted variation in life cycles across locations that qualitatively matches observed natural phenology. Seed dormancy had larger effects on life-cycle length than floral repression, and results suggest that a genetic cline in dormancy maintains a life-cycle length of 1 year across the geographic range of this species. By integrating across life stages, this approach demonstrates how genetic variation in one transition can influence subsequent transitions and the geographic distribution of life cycles more generally.", 
"It has long been known that adaptive evolution can occur through genetic mutations in DNA sequence, but it is unclear whether adaptive evolution can occur through analogous epigenetic mechanisms, such as through DNA methylation. If epigenetic variation contributes directly to evolution, species under threat of disease, invasive competition, climate change or other stresses would have greater stores of variation from which to draw. We looked for evidence of natural selection acting on variably methylated DNA sites using population genomic analysis across three climatologically distinct populations of valley oaks. We found patterns of genetic and epigenetic differentiations that indicate local adaptation is operating on large portions of the oak genome. While CHG methyl polymorphisms are not playing a significant role and would make poor targets for natural selection, our findings suggest that CpG methyl polymorphisms as a whole are involved in local adaptation, either directly or through linkage to regions under selection.", 
"Much work has shown that the environment can induce non-genetic changes in phenotype that span multiple generations. Theory predicts that predictable environmental variation selects for both increased within-and across-generation responses. Yet, to the best of our knowledge, there are no empirical tests of this prediction. We explored the relationship between within-versus across-generation plasticity by evaluating the influence of predator cues on the life-history traits of Daphnia ambigua. We measured the duration of predator-induced transgenerational effects, determined when transgenerational responses are induced, and quantified the cues that activate transgenerational plasticity. We show that predator exposure during embryonic development causes earlier maturation and increased reproductive output. Such effects are detectable two generations removed from predator exposure and are similar in magnitude in response to exposure to cues emitted by injured conspecifics. Moreover, all experimental contexts and traits yielded a negative correlation between within-versus across-generation responses. That is, responses to predator cues within- and across-generations were opposite in sign and magnitude. Although many models address transgenerational plasticity, none of them explain this apparent negative relationship between within- and across-generation plasticities. Our results highlight the need to refine the theory of transgenerational plasticity.", 
"Environmentally induced phenotypic plasticity may be a critical component of response to changing environments. We examined local differentiation and adaptive phenotypic plasticity in response to elevated temperature in half-sib lines collected across an elevation gradient for the alpine herb, Wahlenbergia ceracea. Using Amplified Fragment Length Polymorphism (AFLP), we found low but significant genetic differentiation between low- and high-elevation seedlings, and seedlings originating from low elevations grew faster and showed stronger temperature responses (more plasticity) than those from medium and high elevations. Furthermore, plasticity was more often adaptive for plants of low-elevation origin and maladaptive for plants of high elevation. With methylation sensitive-AFLP (MS-AFLP), we revealed an increase in epigenetic variation in response to temperature in low-elevation seedlings. Although we did not find significant direct correlations between MS-AFLP loci and phenotypes, our results demonstrate that adaptive plasticity in temperature response to warming varies over fine spatial scales and suggest the involvement of epigenetic mechanisms in this response.", 
"Phenotypic plasticity is an important mechanism for populations to buffer themselves from environmental change. While it has long been appreciated that natural populations possess genetic variation in the extent of plasticity, a surge of recent evidence suggests that epigenetic variation could also play an important role in shaping phenotypic responses. Compared with genetic variation, epigenetic variation is more likely to have higher spontaneous rates of mutation and a more sensitive reaction to environmental inputs. In our review, we first provide an overview of recent studies on epigenetically encoded thermal plasticity in animals to illustrate environmentally-mediated epigenetic effects within and across generations. Second, we discuss the role of epigenetic effects during adaptation by exploring population epigenetics in natural animal populations. Finally, we evaluate the evolutionary potential of epigenetic variation depending on its autonomy from genetic variation and its transgenerational stability. Although many of the causal links between epigenetic variation and phenotypic plasticity remain elusive, new data has explored the role of epigenetic variation in facilitating evolution in natural populations. This recent progress in ecological epigenetics will be helpful for generating predictive models of the capacity of organisms to adapt to changing climates.", 
"Methylation of DNA cytosines affects whether transposons are silenced and genes are expressed, and is a major epigenetic mechanism whereby plants respond to environmental change. Analyses of methylation-sensitive amplification polymorphism (MS-AFLP or MSAP) have been often used to assess methyl-cytosine changes in response to stress treatments and, more recently, in ecological studies of wild plant populations. MSAP technique does not require a sequenced reference genome and provides many anonymous loci randomly distributed over the genome for which the methylation status can be ascertained. Scoring of MSAP data, however, is not straightforward, and efforts are still required to standardize this step to make use of the potential to distinguish between methylation at different nucleotide contexts. Furthermore, it is not known how accurately MSAP infers genome-wide cytosine methylation levels in plants. Here, we analyse the relationship between MSAP results and the percentage of global cytosine methylation in genomic DNA obtained by HPLC analysis. A screening of literature revealed that methylation of cytosines at cleavage sites assayed by MSAP was greater than genome-wide estimates obtained by HPLC, and percentages of methylation at different nucleotide contexts varied within and across species. Concurrent HPLC and MSAP analyses of DNA from 200 individuals of the perennial herb Helleborus foetidus confirmed that methyl-cytosine was more frequent in CCGG contexts than in the genome as a whole. In this species, global methylation was unrelated to methylation at the inner CG site. We suggest that global HPLC and context-specific MSAP methylation estimates provide complementary information whose combination can improve our current understanding of methylation-based epigenetic processes in nonmodel plants.", 
"Testing for conserved and novel mechanisms underlying phenotypic evolution requires a diversity of genomes available for comparison spanning multiple independent lineages. For example, complex social behavior in insects has been investigated primarily with eusocial lineages, nearly all of which are Hymenoptera. If conserved genomic influences on sociality do exist, we need data from a wider range of taxa that also vary in their levels of sociality. Here, we present the assembled and annotated genome of the subsocial beetle Nicrophorus vespilloides, a species long used to investigate evolutionary questions of complex social behavior. We used this genome to address two questions. First, do aspects of life history, such as using a carcass to breed, predict overlap in gene models more strongly than phylogeny? We found that the overlap in gene models was similar between N. vespilloides and all other insect groups regardless of life history. Second, like other insects with highly developed social behavior but unlike other beetles, does N. vespilloides have DNA methylation? We found strong evidence for an active DNA methylation system. The distribution of methylation was similar to other insects with exons having the most methylated C pGs. Methylation status appears highly conserved; 85% of the methylated genes in N. vespilloides are also methylated in the hymentopteran Nasonia vitripennis. The addition of this genome adds a coleopteran resource to answer questions about the evolution and mechanistic basis of sociality and to address questions about the potential role of methylation in social behavior.", 
"Telomeres are emerging as a biomarker for ageing and survival, and are likely important in shaping life-history trade-offs. In particular, telomere length with which one starts in life has been linked to lifelong survival, suggesting that early telomere dynamics are somehow related to life-history trajectories. This result highlights the importance of determining the extent to which telomere length is inherited, as a crucial factor determining early life telomere length. Given the scarcity of species for which telomere length inheritance has been studied, it is pressing to assess the generality of telomere length inheritance patterns. Further, information on how this pattern changes over the course of growth in individuals living under natural conditions should provide some insight on the extent to which environmental constraints also shape telomere dynamics. To fill this gap partly, we followed telomere inheritance in a population of king penguins (Aptenodytes patagonicus). We tested for paternal and maternal influence on chick initial telomere length (10 days old after hatching), and how these relationships changed with chick age (at 70, 200 and 300 days old). Based on a correlative approach, offspring telomere length was positively associated with maternal telomere length early in life (at 10 days old). However, this relationship was not significant at older ages. These data suggest that telomere length in birds is maternally inherited. Nonetheless, the influence of environmental conditions during growth remained an important factor shaping telomere length, as the maternal link disappeared with chicks' age.", 
"Transgenerational effects can buffer populations against environmental change, yet little is known about underlying mechanisms, their persistence or the influence of environmental cue timing. We investigated mitochondrial respiratory capacity (MRC) and gene expression of marine sticklebacks that experienced acute or developmental acclimation to simulated ocean warming (21 degrees C) across three generations. Previous work showed that acute acclimation of grandmothers to 21 degrees C led to lower (optimized) offspring MRCs. Here, developmental acclimation of mothers to 21 degrees C led to higher, but more efficient offspring MRCs. Offspring with a 21 degrees C x 17 degrees C grandmother-mother environment mismatch showed metabolic compensation: their MRCs were as low as offspring with a 17 degrees C thermal history across generations. Transcriptional analyses showed primarily maternal but also grandmaternal environment effects: genes involved in metabolism and mitochondrial protein biosynthesis were differentially expressed when mothers developed at 21 degrees C, whereas 21 degrees C grandmothers influenced genes involved in hemostasis and apoptosis. Genes involved in mitochondrial respiration all showed higher expression when mothers developed at 21 degrees and lower expression in the 21 degrees C x 17 degrees C group, matching the phenotypic pattern for MRCs. Our study links transcriptomics to physiology under climate change, and demonstrates that mechanisms underlying transgenerational effects persist across multiple generations with specific outcomes depending on acclimation type and environmental mismatch between generations.", 
"The effects from multigenerational exposures to engineered nanoparticles (ENPs) in their pristine and transformed states are currently unknown despite such exposures being an increasingly common scenario in natural environments. Here, we examine how exposure over 10 generations affects the sensitivity of the nematode Caenorhabditis elegans to pristine and sulfidized Ag ENPs and AgNO3. We also include populations that were initially exposed over six generations but kept unexposed for subsequent four generations to allow recovery from exposure. Toxicity of the different silver forms decreased in the order AgNO3, Ag ENPs and Ag2S ENPs. Continuous exposure to Ag ENPs and AgNO3 caused pronounced sensitization (approx. 10-fold) in the F2 generation, which was sustained until F10. This sensitization was less pronounced for Ag2S ENP exposures, indicating different toxicity mechanisms. Subtle changes in size and lifespan were also measured. In the recovery populations, the sensitivity to Ag ENPs and AgNO3 resulting from the initial multigenerational exposure persisted. Their response sensitivity for all endpoints was most closely related to the last ancestral exposed generation (F5), rather than unexposed controls. The mechanisms of transgenerational transfer of sensitivity are probably organized through the epigenome, and we encourage others to investigate such effects as a priority for mechanistic toxicology.", 
"Epigenetic variation has been proposed to contribute to the success of asexual plants, either as a contributor to phenotypic plasticity or by enabling transient adaptation via selection on transgenerationally stable, but reversible, epialleles. While recent studies in experimental plant populations have shown the potential for epigenetic mechanisms to contribute to adaptive phenotypes, it remains unknown whether heritable variation in ecologically relevant traits is at least partially epigenetically determined in natural populations. Here, we tested the hypothesis that DNA methylation variation contributes to heritable differences in flowering time within a single widespread apomictic clonal lineage of the common dandelion (Taraxacum officinale s. lat.). Apomictic clone members of the same apomictic lineage collected from different field sites showed heritable differences in flowering time, which was correlated with inherited differences in methylation-sensitive AFLP marker profiles. Differences in flowering between apomictic clone members were significantly reduced after in vivo demethylation using the DNA methyltransferase inhibitor zebularine. This synchronization of flowering times suggests that flowering time divergence within an apomictic lineage was mediated by differences in DNA methylation. While the underlying basis of the methylation polymorphism at functional flowering time-affecting loci remains to be demonstrated, our study shows that epigenetic variation contributes to heritable phenotypic divergence in ecologically relevant traits in natural plant populations. This result also suggests that epigenetic mechanisms can facilitate adaptive divergence within genetically uniform asexual lineages.", 
"Variation in resource availability commonly exerts strong effects on fitness-related traits in wild animals. However, we know little about the molecular mechanisms that mediate these effects, or about their persistence over time. To address these questions, we profiled genome-wide whole-blood DNA methylation levels in two sets of wild baboons: (i) 'wild-feeding' baboons that foraged naturally in a savanna environment and (ii) 'Lodge' baboons that had ready access to spatially concentrated human food scraps, resulting in high feeding efficiency and low daily travel distances. We identified 1014 sites (0.20% of sites tested) that were differentially methylated between wild-feeding and Lodge baboons, providing the first evidence that resource availability shapes the epigenome in a wild mammal. Differentially methylated sites tended to occur in contiguous stretches (i.e., in differentially methylated regions or DMRs), in promoters and enhancers, and near metabolism-related genes, supporting their functional importance in gene regulation. In agreement, reporter assay experiments confirmed that methylation at the largest identified DMR, located in the promoter of a key glycolysis-related gene, was sufficient to causally drive changes in gene expression. Intriguingly, all dispersing males carried a consistent epigenetic signature of their membership in a wild-feeding group, regardless of whether males dispersed into or out of this group as adults. Together, our findings support a role for DNA methylation in mediating ecological effects on phenotypic traits in the wild and emphasize the dynamic environmental sensitivity of DNA methylation levels across the life course.", 
"Epigenetic modifications are expected to occur at a much faster rate than genetic mutations, potentially causing isolated populations to stochastically drift apart, or if they are subjected to different selective regimes, to directionally diverge. A high level of genome-wide epigenetic divergence between individuals occupying distinct habitats is therefore predicted. Here, we introduce bisulfite-converted restriction site associated DNA sequencing (bsRADseq), an approach to quantify the level of DNA methylation differentiation across multiple individuals. This reduced representation method is flexible in the extent of DNA sequence interrogated. We showcase its applicability in three natural systems, each comprising individuals adapted to divergent environments: a diploid plant (Heliosperma, Caryophyllaceae), a tetraploid plant (Dactylorhiza, Orchidaceae) and an animal (Gasterosteusaculeatus, Gasterosteidae). We present a robust bioinformatic pipeline, combining tools for RAD locus assembly, SNP calling, bisulfite-converted read mapping and DNA methylation calling to analyse bsRADseq data with or without a reference genome. Importantly, our approach accurately distinguishes between SNPs and methylation polymorphism (SMPs). Although DNA methylation frequency between different positions of a genome varies widely, we find a surprisingly high consistency in the methylation profile between individuals thriving in divergent ecological conditions, particularly in Heliosperma. This constitutive stability points to significant molecular or developmental constraints acting on DNA methylation variation. Altogether, by combining the flexibility of RADseq with the accuracy of bisulfite sequencing in quantifying DNA methylation, the bsRADseq methodology and our bioinformatic pipeline open up the opportunity for genome-wide epigenetic investigations of evolutionary and ecological relevance in non-model species, independent of their genomic features.", 
"The growing knowledge about the influence of transposable elements (TEs) on (a) long-term genome and transcriptome evolution; (b) genomic, transcriptomic and epigenetic variation within populations; and (c) patterns of somatic genetic differences in individuals continues to spur the interest of evolutionary biologists in the role of TEs in adaptive evolution. As TEs can trigger a broad range of molecular variation in a population with potentially severe fitness and phenotypic consequences for individuals, different mechanisms evolved to keep TE activity in check, allowing for a dynamic interplay between the host, its TEs and the environment in evolution. Here, we review evidence for adaptive phenotypic changes associated with TEs and the basic molecular mechanisms by which the underlying genetic changes arise: (a) domestication, (b) exaptation, (c) host gene regulation, (d) TE-mediated formation of intronless gene copies-so-called retrogenes and (e) overall increased genome plasticity. Furthermore, we review and discuss how the stress-dependent incapacitation of defence mechanisms against the activity of TEs might facilitate adaptive responses to environmental challenges and how such mechanisms might be particularly relevant in species frequently facing novel environments, such as invasive, pathogenic or parasitic species.", 
"The decreasing cost and increasing scope and power of emerging genomic technologies are reshaping the field of molecular ecology. However, many modern genomic approaches (e.g., RAD-seq) require large amounts of high-quality template DNA. This poses a problem for an active branch of conservation biology: genetic monitoring using minimally invasive sampling (MIS) methods. Without handling or even observing an animal, MIS methods (e.g., collection of hair, skin, faeces) can provide genetic information on individuals or populations. Such samples typically yield low-quality and/or quantities of DNA, restricting the type of molecular methods that can be used. Despite this limitation, genetic monitoring using MIS is an effective tool for estimating population demographic parameters and monitoring genetic diversity in natural populations. Genetic monitoring is likely to become more important in the future as many natural populations are undergoing anthropogenically driven declines, which are unlikely to abate without intensive adaptive management efforts that often include MIS approaches. Here, we profile the expanding suite of genomic methods and platforms compatible with producing genotypes from MIS, considering factors such as development costs and error rates. We evaluate how powerful new approaches will enhance our ability to investigate questions typically answered using genetic monitoring, such as estimating abundance, genetic structure and relatedness. As the field is in a period of unusually rapid transition, we also highlight the importance of legacy data sets and recommend how to address the challenges of moving between traditional and next-generation genetic monitoring platforms. Finally, we consider how genetic monitoring could move beyond genotypes in the future. For example, assessing microbiomes or epigenetic markers could provide a greater understanding of the relationship between individuals and their environment.", 
"ObjectivesDifferences in DNA methylation have been associated with early life adversity, suggesting that alterations in methylation function as one pathway through which adverse early environments are biologically embedded. This study examined associations between exposure to institutional care, quantified as the proportion of time in institutional care at specified follow-up assessment ages, and DNA methylation status in two stress-related genes: FKBP5 and SLC6A4. Materials and MethodsWe analyzed data from the Bucharest Early Intervention Project, which is a prospective study in which children reared in institutional settings were randomly assigned (mean age 22 months) to either newly created foster care or care as usual (to remain in their current placement) and prospectively followed. A group of children from the same geographic area, with no history of institutionalized caregiving, were also recruited. DNA methylation status was determined in DNA extracted from buccal epithelial cells of children at age 12. ResultsAn inverse association was identified such that more time spent in institutional care was associated with lower DNA methylation at specific CpG sites within both genes. DiscussionThese results suggest a lasting impact of early severe social deprivation on methylation patterns in these genes, and contribute to a growing literature linking early adversity and epigenetic variation in children. Am J Phys Anthropol 161:84-93, 2016.. (c) 2016 Wiley Periodicals, Inc.", 
"DNA methylation is an epigenetic mark that plays an inadequately understood role in gene regulation, particularly in nonmodel species. Because it can be influenced by the environment, DNA methylation may contribute to the ability of organisms to acclimatize and adapt to environmental change. We evaluated the distribution of gene body methylation in reef-building corals, a group of organisms facing significant environmental threats. Gene body methylation in six species of corals was inferred from in silico transcriptome analysis of CpG O/E, an estimate of germline DNA methylation that is highly correlated with patterns of methylation enrichment. Consistent with what has been documented in most other invertebrates, all corals exhibited bimodal distributions of germline methylation suggestive of distinct fractions of genes with high and low levels of methylation. The hypermethylated fractions were enriched with genes with housekeeping functions, while genes with inducible functions were highly represented in the hypomethylated fractions. High transcript abundance was associated with intermediate levels of methylation. In three of the coral species, we found that genes differentially expressed in response to thermal stress and ocean acidification exhibited significantly lower levels of methylation. These results support a link between gene body hypomethylation and transcriptional plasticity that may point to a role of DNA methylation in the response of corals to environmental change.", 
"Recent studies show that epigenetic variation in the form of DNA methylation may serve as a substrate for selection. Theory suggests that heritable epigenetic marks that increase fitness should increase in frequency in a population, and these changes may result in novel morphology, behaviour, or physiology, and ultimately reproductive isolation. Therefore, epigenetic variation might provide the first substrate for selection during the course of evolutionary divergence. This hypothesis predicts that populations in the earliest stages of divergence will differentiate in their methylome prior to any genetic differentiation. While several studies have investigated natural epigenetic variation, empirical studies that test predictions about its role in speciation are surprisingly scarce. Here, we investigate DNA methylation variation using an isoschizomeric digest method, Methyl-Sensitive Amplified Polymorphism, across multiple stages of evolutionary divergence in natural populations of North American stream fishes. We show that epigenetic differentiation between methylomes is greater than genetic divergence among closely related populations across two river drainages. Additionally, we demonstrate that epigenetic divergence is a stronger predictor of the strength of behavioural reproductive isolation and suggest that changes in the methylome could influence the evolution of reproductive isolation between species. Our findings suggest a role for epigenetics not only in the initiation of divergence, but also in the maintenance of species boundaries over greater evolutionary timescales.", 
"The development of multicellular organisms involves a delicate interplay between genetic and environmental influences. It is often useful to think of developmental systems as integrating available sources of information about current conditions to produce organisms. Genes and inherited physiology provide cues, as does the state of the environment during development. The integration systems themselves are under genetic control and subject to Darwinian selection, so we expect them to evolve to produce organisms that fit well with current ecological (including social) conditions. We argue for the scientific value of this explicitly informational perspective by providing detailed examples of how it can elucidate taxonomically diverse phenomena. We also present a general framework for linking genetic and phenotypic variation from an informational perspective. This application of Darwinian logic at the organismal level can elucidate genetic influences on phenotypic variation in novel and counterintuitive ways.", 
"Organisms can adapt to variable environments by using environmental cues to modulate developmental gene expression. In principle, maternal influences can adaptively adjust offspring phenotype when early life and adult environments match, but they may be maladaptive when future environments are not predictable. One of the best-studied 'maternal effects' is through modification of the offspring's hypothalamic-pituitary-adrenal (HPA) axis, the neuroendocrine system that controls responses to stress. In addition to the direct transfer of glucocorticoids from mother to offspring, offspring HPA function and other phenotypes can also be affected by epigenetic modifications like DNA methylation of the glucocorticoid receptor promoter. Here we examine how among-year variation in rainfall is related to DNA methylation during development and fitness in adulthood in the superb starling (Lamprotornis superbus), which lives in a climatically unpredictable environment where early life and adult environments are unlikely to match. We found that DNA methylation in the putative promoter of the glucocorticoid receptor gene is reduced in chicks - particularly in males - born following drier prebreeding periods. Additionally, DNA methylation is lower in males that become breeders than those that never breed. However, there is no relationship in females between DNA methylation and the likelihood of dispersing from the natal group to breed elsewhere. These results suggest that early life conditions may positively affect fitness in a sex-specific manner through chemical modification of an HPA-associated gene. This study is the first to show that epigenetic modifications during early life may influence the fitness of free-living organisms adapted to unpredictable environments.", 
"Personality traits are heritable and respond to natural selection, but are at the same time influenced by the ontogenetic environment. Epigenetic effects, such as DNA methylation, have been proposed as a key mechanism to control personality variation. However, to date little is known about the contribution of epigenetic effects to natural variation in behaviour. Here, we show that great tit (Parus major) lines artificially selected for divergent exploratory behaviour for four generations differ in their DNA methylation levels at the dopamine receptor D4 (DRD4) gene. This D4 receptor is statistically associated with personality traits in both humans and nonhuman animals, including the great tit. Previous work in this songbird failed to detect functional genetic polymorphisms within DRD4 that could account for the gene-trait association. However, our observation supports the idea that DRD4 is functionally involved in exploratory behaviour but that its effects are mediated by DNA methylation. While the exact mechanism underlying the transgenerational consistency of DRD4 methylation remains to be elucidated, this study shows that epigenetic mechanisms are involved in shaping natural variation in personality traits. We outline how this first finding provides a basis for investigating the epigenetic contribution to personality traits in natural systems and its subsequent role for understanding the ecology and evolution of behavioural consistency.", 
"Gene sequence similarity due to shared ancestry after a duplication event, that is paralogy, complicates the assessment of genetic variation, as sequences originating from paralogs can be difficult to distinguish. These confounded sequences are often removed prior to further analyses, leaving the underlying loci uncharacterized. Salmonids have only partially rediploidized subsequent to a whole-genome duplication; residual tetrasomic inheritance has been observed in males. We present a maximum-likelihood-based method to resolve confounded paralogous loci by observing the segregation of alleles in gynogenetic haploid offspring and demonstrate its effectiveness by constructing two linkage maps for chum salmon (Oncorhynchus keta), with and without these newly resolved loci. We find that the resolved paralogous loci are not randomly distributed across the genome. A majority are clustered in expanded subtelomeric regions of 14 linkage groups, suggesting a significant fraction of the chum salmon genome may be missed by the exclusion of paralogous loci. Transposable elements have been proposed as drivers of genome evolution and, in salmonids, may have an important role in the rediploidization process by driving differentiation between homeologous chromosomes. Consistent with that hypothesis, we find a reduced fraction of transposable element annotations among paralogous loci, and these loci predominately occur in the genomic regions that lag in the rediploidization process.", 
"Heat-shock proteins (Hsps) and their cognates are primary mitigators of cell stress. With increasingly severe impacts of climate change and other human modifications of the biosphere, the ability of the heat-shock system to affect evolutionary fitness in environments outside the laboratory and to evolve in response is topic of growing importance. Since the last major reviews, several advances have occurred. First, demonstrations of the heat-shock response outside the laboratory now include many additional taxa and environments. Many of these demonstrations are only correlative, however. More importantly, technical advances in omic quantification of nucleic acids and proteins, genomewide association analysis, and manipulation of genes and their expression have enabled the field to move beyond correlation. Several consequent advances are already evident: The pathway from heat-shock gene expression to stress tolerance in nature can be extremely complex, mediated through multiple biological processes and systems, and even multiple species. The underlying genes are more numerous, diverse and variable than previously appreciated, especially with respect to their regulatory variation and epigenetic changes. The impacts and limitations (e.g., due to trade-offs) of natural selection on these genes have become more obvious and better established. At last, as evolutionary capacitors, Hsps may have distinctive impacts on the evolution of other genes and ecological consequences.", 
"Resetting of epigenetic marks, such as DNA methylation, in germ cells or early embryos is not always complete. Epigenetic states may therefore persist, decay or accumulate across generations. In spite of mounting empirical evidence for incomplete resetting, it is currently poorly understood whether it simply reflects stochastic noise or plays an adaptive role in phenotype determination. Here, we use a simple model to show that incomplete resetting can be adaptive in heterogeneous environments. Transmission of acquired epigenetic states prevents mismatched phenotypes when the environment changes infrequently relative to generation time and when maternal and environmental cues are unreliable. We discuss how these results may help to interpret the emerging data on transgenerational epigenetic inheritance in plants and animals.", 
"Genomes of invertebrates and vertebrates exhibit highly divergent patterns of DNA methylation. Invertebrate genomes tend to be sparsely methylated, and DNA methylation is mostly targeted to a subset of transcription units (gene bodies). In a drastic contrast, vertebrate genomes are generally globally and heavily methylated, punctuated by the limited local hypo-methylation of putative regulatory regions such as promoters. These genomic differences also translate into functional differences in DNA methylation and gene regulation. Although promoter DNA methylation is an important regulatory component of vertebrate gene expression, its role in invertebrate gene regulation has been little explored. Instead, gene body DNA methylation is associated with expression of invertebrate genes. However, the evolutionary steps leading to the differentiation of invertebrate and vertebrate genomic DNA methylation remain unresolved. Here we analyzed experimentally determined DNA methylation maps of several species across the invertebrate-vertebrate boundary, to elucidate how vertebrate gene methylation has evolved. We show that, in contrast to the prevailing idea, a substantial number of promoters in an invertebrate basal chordate Ciona intestinalis are methylated. Moreover, gene expression data indicate significant, epigenomic context-dependent associations between promoter methylation and expression in C. intestinalis. However, there is no evidence that promoter methylation in invertebrate chordate has been evolutionarily maintained across the invertebrate-vertebrate boundary. Rather, body-methylated invertebrate genes preferentially obtain hypo-methylated promoters among vertebrates. Conversely, promoter methylation is preferentially found in lineage- and tissue-specific vertebrate genes. These results provide important insights into the evolutionary origin of epigenetic regulation of vertebrate gene expression.", 
"Animal and plant centromeres are embedded in repetitive satellite DNA, but are thought to be epigenetically specified. To define genetic characteristics of centromeres, we surveyed satellite DNA from diverse eukaryotes and identified variation in <10-bp dyad symmetries predicted to adopt non-B-form conformations. Organisms lacking centromeric dyad symmetries had binding sites for sequence-specific DNA-binding proteins with DNA-bending activity. For example, human and mouse centromeres are depleted for dyad symmetries, but are enriched for non-B-form DNA and are associated with binding sites for the conserved DNA-binding protein CENP-B, which is required for artificial centromere function but is paradoxically nonessential. We also detected dyad symmetries and predicted non-B-form DNA structures at neocentromeres, which form at ectopic loci. We propose that centromeres form at non-B-form DNA because of dyad symmetries or are strengthened by sequence-specific DNA binding proteins. This may resolve the CENP-B paradox and provide a general basis for centromere specification.", 
"Epigenetic mechanisms such as changes in DNA methylation have the potential to affect the resilience of species to climate change, but little is known about the response of the methylome to changes in environmental temperature in animals. Using reduced representation bisulfite sequencing, we assessed the effects of development temperature and adult acclimation temperature on DNA methylation levels in threespine stickleback (Gasterosteus aculeatus). Across all treatments, we identified 2130 differentially methylated cytosines distributed across the genome. Both increases and decreases in temperature during development and with thermal acclimation in adults increased global DNA methylation levels. Approximately 25% of the differentially methylated regions (DMRs) responded to both developmental temperature and adult thermal acclimation, and 50 DMRs were common to all treatments, demonstrating a core response of the epigenome to thermal change at multiple time scales. We also identified differentially methylated loci that were specific to a particular developmental or adult thermal response, which could facilitate the accumulation of epigenetic variation between natural populations that experience different thermal regimes. These data demonstrate that thermal history can have long-lasting effects on the epigenome, highlighting the role of epigenetic modifications in the response to temperature change across multiple time scales.", 
"The diversity of sex chromosomes among amniotes is the product of independent evolution of different systems in different lineages, defined by novel sex-determining genes. Convergent evolution is very common, suggesting that some genes are particularly adept at taking on a sex-determining role. Comparative gene mapping, and more recently whole genome sequencing, have now turned up other surprising relationships; different regions of the amniote genome that have become sex determining in some taxa seem to share synteny, or share sequence, in others. Is this, after all, evidence that these regions were once linked in a super-sex chromosome that underwent multiple fission in different ways in different amniote lineages? Or does it signify that special properties of sex chromosomes (paucity of active genes, low recombination, epigenetic regulation to achieve dosage compensation) predispose particular chromosomes to a sex-determining role?", 
" ", 
"Epigenetic changes can occur due to extracellular environmental conditions. Consequently, epigenetic mechanisms can play an intermediate role to translate environmental signals to intracellular changes. Such a role might be particularly important in plants, which often show strong local adaptation and have the potential for heritable epigenetic states. However, little is currently known about the role of epigenetic variation in the ecological mechanisms of adaptation. Here, we used multivariate redundancy analyses to examine genomewide associations between DNA methylation polymorphisms and climate variation in two independent panels of Arabidopsis accessions, including 122 Eurasian accessions as well as in a regional panel of 148 accessions in Sweden. At the single-nucleotide methylation level, climate and space (geographic spatial structure) explain small yet significant amount of variation in both panels. On the other hand, when viewed in a context of genomic clusters of methylated and unmethylated cytosines, climate and space variables explain much greater amounts of variation in DNA methylation than those explained by variation at the single-nucleotide level. We found that the single-nucleotide methylation polymorphisms with the strongest associations with climate were enriched in transposable elements and in potentially RNA-directed methylation contexts. When viewed in the context of genomic clusters, variation of DNA methylation at different sequence contexts exhibit distinctive segregation along different axes of variation in the redundancy analyses. Genomewide methylation showed much stronger associations with climate within the regional panel (Sweden) compared to the global (Eurasia). Together, these findings indicate that genetic and epigenetic variation across the genome may play a role in response to climate conditions and local adaptation.", 
"The three-spined stickleback (Gasterosteus aculeatus) represents a convenient model to study microevolution-adaptation to a freshwater environment. Although genetic adaptations to freshwater environments are well-studied, epigenetic adaptations have attracted little attention. In this work, we investigated the role of DNA methylation in the adaptation of the marine stickleback population to freshwater conditions. DNA methylation profiling was performed in marine and freshwater populations of sticklebacks, as well as in marine sticklebacks placed into a freshwater environment and freshwater sticklebacks placed into seawater. We showed that the DNA methylation profile after placing a marine stickleback into fresh water partially converged to that of a freshwater stickleback. For six genes including ATP4A ion pump and NELL1, believed to be involved in skeletal ossification, we demonstrated similar changes in DNA methylation in both evolutionary and short-term adaptation. This suggested that an immediate epigenetic response to freshwater conditions can be maintained in freshwater population. Interestingly, we observed enhanced epigenetic plasticity in freshwater sticklebacks that may serve as a compensatory regulatory mechanism for the lack of genetic variation in the freshwater population. For the first time, we demonstrated that genes encoding ion channels KCND3, CACNA1FB, and ATP4A were differentially methylated between the marine and the freshwater populations. Other genes encoding ion channels were previously reported to be under selection in freshwater populations. Nevertheless, the genes that harbor genetic and epigenetic changes were not the same, suggesting that epigenetic adaptation is a complementary mechanism to selection of genetic variants favorable for freshwater environment.", 
"Epigenetic modifications, such as DNA methylation or histone modifications, can be transmitted between cellular or organismal generations. However, there are no experiments measuring their role in adaptation, so here we use experimental evolution to investigate how epigenetic variation can contribute to adaptation. We manipulated DNA methylation and histone acetylation in the unicellular green alga Chlamydomonas reinhardtii both genetically and chemically to change the amount of epigenetic variation generated or transmitted in adapting populations in three different environments (salt stress, phosphate starvation, and high CO2) for two hundred asexual generations. We find that reducing the amount of epigenetic variation available to populations can reduce adaptation in environments where it otherwise happens. From genomic and epigenomic sequences from a subset of the populations, we see changes in methylation patterns between the evolved populations over-represented in some functional categories of genes, which is consistent with some of these differences being adaptive. Based on whole genome sequencing of evolved clones, the majority of DNA methylation changes do not appear to be linked to cis-acting genetic mutations. Our results show that transgenerational epigenetic effects play a role in adaptive evolution, and suggest that the relationship between changes in methylation patterns and differences in evolutionary outcomes, at least for quantitative traits such as cell division rates, is complex.", 
"Hybridization has many and varied impacts on the process of speciation. Hybridization may slow or reverse differentiation by allowing gene flow and recombination. It may accelerate speciation via adaptive introgression or cause near-instantaneous speciation by allopolyploidization. It may have multiple effects at different stages and in different spatial contexts within a single speciation event. We offer a perspective on the context and evolutionary significance of hybridization during speciation, highlighting issues of current interest and debate. In secondary contact zones, it is uncertain if barriers to gene flow will be strengthened or broken down due to recombination and gene flow. Theory and empirical evidence suggest the latter is more likely, except within and around strongly selected genomic regions. Hybridization may contribute to speciation through the formation of new hybrid taxa, whereas introgression of a few loci may promote adaptive divergence and so facilitate speciation. Gene regulatory networks, epigenetic effects and the evolution of selfish genetic material in the genome suggest that the DobzhanskyMuller model of hybrid incompatibilities requires a broader interpretation. Finally, although the incidence of reinforcement remains uncertain, this and other interactions in areas of sympatry may have knock-on effects on speciation both within and outside regions of hybridization.", 
"Experimental evolution is the study of evolutionary processes occurring in experimental populations in response to conditions imposed by the experimenter. This research approach is increasingly used to study adaptation, estimate evolutionary parameters, and test diverse evolutionary hypotheses. Long applied in vaccine development, experimental evolution also finds new applications in biotechnology. Recent technological developments provide a path towards detailed understanding of the genomic and molecular basis of experimental evolutionary change, while new findings raise new questions that can be addressed with this approach. However, experimental evolution has important limitations, and the interpretation of results is subject to caveats resulting from small population sizes, limited timescales, the simplified nature of laboratory environments, and, in some cases, the potential to misinterpret the selective forces and other processes at work.", 
"Epigenetics investigates heritable changes in gene expression that occur without changes in DNA sequence. Several epigenetic mechanisms, including DNA methylation and histone modifications, can change genome function under exogenous influence. We review current evidence indicating that epigenetic alterations mediate effects caused by exposure to environmental toxicants. Results obtained from animal models indicate that in utero or early-life environmental exposures produce effects that can be inherited transgenerationally and are accompanied by epigenetic alterations. The search for human equivalents of the epigenetic mechanisms identified in animal models is under way. Recent investigations have identified a number of environmental toxicants that cause altered methylation of human repetitive elements or genes. Some exposures can alter epigenetic states and the same and/or similar epigenetic alterations can be found in patients with the disease of concern. On the basis of current evidence, we propose possible models for the interplay between environmental exposures and the human epigenome. Several investigations have examined the relationship between exposure to environmental chemicals and epigenetics, and have identified toxicants that modify epigenetic states. Whether environmental exposures have transgenerational epigenetic effects in humans remains to be elucidated. In spite of the current limitations, available evidence supports the concept that epigenetics holds substantial potential for furthering our understanding of the molecular mechanisms of environmental toxicants, as well as for predicting health-related risks due to conditions of environmental exposure and individual susceptibility. Heredity (2010) 105, 105-112; doi:10.1038/hdy.2010.2; published online 24 February 2010", 
"Transcription, translation and subsequent protein modification represent the transfer of genetic information from the archival copy of DNA to the short-lived messenger RNA, usually with subsequent production of protein. Although all cells in an organism contain essentially the same DNA, cell types and functions differ because of qualitative and quantitative differences in their gene expression. Thus, control of gene expression is at the heart of differentiation and development. Epigenetic processes, including DNA methylation, histone modification and various RNA-mediated processes, are thought to influence gene expression chiefly at the level of transcription; however, other steps in the process (for example, translation) may also be regulated epigenetically. The following paper will outline the role epigenetics is believed to have in influencing gene expression. Heredity (2010) 105, 4-13; doi:10.1038/hdy.2010.54; published online 12 May 2010", 
"During the past decade there has been a tremendous resurgence of interest in polyploidy that has in large part been stimulated by the development of increasingly powerful genetic and genomic tools. The result has been numerous new insights into the genomic and genetic consequences of polyploidy. The plethora of new discoveries has dramatically reshaped traditional views and concomitantly revealed that polyploidy is a highly dynamic and ubiquitous process. These recent advances in our understanding of polyploidy have stimulated numerous reviews, most focused on the various genetic, epigenetic, and genomic consequences of polyploid evolution. Whereas genetic and genomic attributes of polyploidization have received considerable attention, other crucial areas of polyploid evolution have received much less (e.g., ecology, pollination biology, physiology). The focus of this paper is not to review again recent discoveries, but to emphasize what we do not yet know about polyploidy, which despite all that has been learned about genome doubling is still an enormous amount. Our list is not meant to be comprehensive, but includes a range of topics that we have placed in several general categories, including mode of formation, ecological and physiological consequences, and genomic rules. Questions include: What is (are) the most frequent mechanism(s) of polyploidization? What factors promote/facilitate polyploidization? What factors favor autopolyploid vs. allopolyploid formation? Do multiple origins result in lineages with differing evolutionary trajectories and/or cryptic species? Our major goals are to stimulate discussion and promote further research.", 
"Rapidly accumulating evidence shows that herbivore and pathogen attack of plants can generate particular defense phenotypes across generations. What was once thought to be an oddity of plant defense induction now appears to be a taxonomically widespread phenomenon with strong potential to impact the ecology and evolution of species interactions. DNA methylation, histone modifications, and small RNAs each contribute to transgenerational defense initiation; examples in several species demonstrate that this induction can last for multiple generations. Priming of the offspring generation for more rapid induction following subsequent attack has also been reported. The extent to which transgenerational induction is predictable, detectable in nature, and subject to manipulation will determine the ability of researchers to decipher its role in plant-herbivore and plant-pathogen interactions.", 
"Aside from its selective role in filtering inter-individual variation during evolution by natural selection, the environment also plays an instructive role in producing variation during development. External environmental cues can influence developmental rates and/or trajectories and lead to the production of distinct phenotypes from the same genotype. This can result in a better match between adult phenotype and selective environment and thus represents a potential solution to problems posed by environmental fluctuation. The phenomenon is called adaptive developmental plasticity. The study of developmental plasticity integrates different disciplines (notably ecology and developmental biology) and analyses at all levels of biological organization, from the molecular regulation of changes in organismal development to variation in phenotypes and fitness in natural populations. Here, we focus on recent advances and examples from morphological traits in animals to provide a broad overview covering (i) the evolution of developmental plasticity, as well as its relevance to adaptive evolution, (ii) the ecological significance of alternative environmentally induced phenotypes, and the way the external environment can affect development to produce them, (iii) the molecular mechanisms underlying developmental plasticity, with emphasis on the contribution of genetic, physiological and epigenetic factors, and (iv) current challenges and trends, including the relevance of the environmental sensitivity of development to studies in ecological developmental biology, biomedicine and conservation biology.", 
"Organisms often respond to environmental changes by producing alternative phenotypes. Epigenetic processes such as DNA methylation may contribute to environmentally induced phenotypic variation by modifying gene expression. Changes in DNA methylation, unlike DNA mutations, can be influenced by the environment; they are stable at the time scale of an individual and present different levels of heritability. These characteristics make DNA methylation a potentially important molecular process to respond to environmental change. The aim of this review is to present the implications of DNA methylation on phenotypic variations driven by environmental changes. More specifically, we explore epigenetic concepts concerning phenotypic change in response to the environment and heritability of DNA methylation, namely the Baldwin effect and genetic accommodation. Before addressing this point, we report major differences in DNA methylation across taxa and the role of this modification in producing and maintaining environmentally induced phenotypic variation. We also present the different methods allowing the detection of methylation polymorphism. We believe this review will be helpful to molecular ecologists, in that it highlights the importance of epigenetic processes in ecological and evolutionary studies.", 
"Nongenetic inheritance is a potentially important but poorly understood factor in population responses to rapid environmental change. Accumulating evidence indicates that nongenetic inheritance influences a diverse array of traits in all organisms and can allow for the transmission of environmentally induced phenotypic changes (acquired traits), as well as spontaneously arising and highly mutable variants. We review models of adaptation to changing environments under the assumption of a broadened model of inheritance that incorporates nongenetic mechanisms of transmission, and survey relevant empirical examples. Theory suggests that nongenetic inheritance can increase the rate of both phenotypic and genetic change and, in some cases, alter the direction of change. Empirical evidence shows that a diversity of phenotypes spanning a continuum from adaptive to pathological can be transmitted nongenetically. The presence of nongenetic inheritance therefore complicates our understanding of evolutionary responses to environmental change. We outline a research program encompassing experimental studies that test for transgenerational effects of a range of environmental factors, followed by theoretical and empirical studies on the population-level consequences of such effects.", 
"Allopolyploidy is an evolutionary and mechanistically intriguing process, in that it entails the reconciliation of two or more sets of diverged genomes and regulatory interactions. In this study, we explored gene expression patterns in interspecific hybrid F-1, and synthetic and natural allopolyploid cotton using RNA-Seq reads from leaf transcriptomes. We determined how the extent and direction of expression level dominance (total level of expression for both homoeologs) and homoeolog expression bias (relative contribution of homoeologs to the transcriptome) changed from hybridization through evolution at the polyploid level and following cotton domestication. Genome-wide expression level dominance was biased toward the A-genome in the diploid hybrid and natural allopolyploids, whereas the direction was reversed in the synthetic allopolyploid. This biased expression level dominance was mainly caused by up-or downregulation of the homoeolog from the 'non-dominant' parent. Extensive alterations in homoeolog expression bias and expression level dominance accompany the initial merger of two diverged diploid genomes, suggesting a combination of regulatory (cis or trans) and epigenetic interactions that may arise and propagate through the transcriptome network. The extent of homoeolog expression bias and expression level dominance increases over time, from genome merger through evolution at the polyploid level. Higher rates of transgressive and novel gene expression patterns as well as homoeolog silencing were observed in natural allopolyploids than in F1 hybrid and synthetic allopolyploid cottons. These observations suggest that natural selection reconciles the regulatory mismatches caused by initial genomic merger, while new gene expression conditions are generated for evaluation by selection. Heredity (2013) 110, 171-180; doi:10.1038/hdy.2012.94; published online 21 November 2012", 
"Epigenetic variation is likely to contribute to the phenotypic plasticity and adaptative capacity of plant species, and may be especially important for long-lived organisms with complex life cycles, including forest trees. Diverse environmental stresses and hybridization/polyploidization events can create reversible heritable epigenetic marks that can be transmitted to subsequent generations as a form of molecular memory. Epigenetic changes might also contribute to the ability of plants to colonize or persist in variable environments. In this review, we provide an overview of recent data on epigenetic mechanisms involved in developmental processes and responses to environmental cues in plant, with a focus on forest tree species. We consider the possible role of forest tree epigenetics as a new source of adaptive traits in plant breeding, biotechnology, and ecosystem conservation under rapid climate change.", 
"Inheritance-the influence of ancestors on the phenotypes of their descendants-translates natural selection into evolutionary change. For the past century, inheritance has been conceptualized almost exclusively as the transmission of DNA sequence variation from parents to offspring in accordance with Mendelian rules, but advances in cell and developmental biology have now revealed a rich array of inheritance mechanisms. This empirical evidence calls for a unified conception of inheritance that combines genetic and nongenetic mechanisms and encompasses the known range of transgenerational effects, including the transmission of genetic and epigenetic variation, the transmission of plastic phenotypes (acquired traits), and the effects of parental environment and genotype on offspring phenotype. We propose a unified theoretical framework based on the Price equation that can be used to model evolution under an expanded inheritance concept that combines the effects of genetic and nongenetic inheritance. To illustrate the utility and generality of this framework, we show how it can be applied to a variety of scenarios, including nontransmissible environmental noise, maternal effects, indirect genetic effects, transgenerational epigenetic inheritance, RNA-mediated inheritance, and cultural inheritance.", 
"The consequences of early developmental conditions for performance in later life are now subjected to convergent interest from many different biological sub-disciplines. However, striking data, largely from the biomedical literature, show that environmental effects experienced even before conception can be transmissible to subsequent generations. Here, we review the growing evidence from natural systems for these cross-generational effects of early life conditions, showing that they can be generated by diverse environmental stressors, affect offspring in many ways and can be transmitted directly or indirectly by both parental lines for several generations. In doing so, we emphasize why early life might be so sensitive to the transmission of environmentally induced effects across generations. We also summarize recent theoretical advancements within the field of developmental plasticity, and discuss how parents might assemble different 'internal' and 'external' cues, even from the earliest stages of life, to instruct their investment decisions in offspring. In doing so, we provide a preliminary framework within the context of adaptive plasticity for understanding inter-generational phenomena that arise from early life conditions.", 
"The relationship between genotype (which is inherited) and phenotype (the target of selection) is mediated by environmental inputs on gene expression, trait development, and phenotypic integration. Phenotypic plasticity or epigenetic modification might influence evolution in two general ways: (1) by stimulating evolutionary responses to environmental change via population persistence or by revealing cryptic genetic variation to selection, and (2) through the process of genetic accommodation, whereby natural selection acts to improve the form, regulation, and phenotypic integration of novel phenotypic variants. We provide an overview of models and mechanisms for how such evolutionary influences may be manifested both for plasticity and epigenetic marking. We point to promising avenues of research, identifying systems that can best be used to address the role of plasticity in evolution, as well as the need to apply our expanding knowledge of genetic and epigenetic mechanisms to our understanding of how genetic accommodation occurs in nature. Our review of a wide variety of studies finds widespread evidence for evolution by genetic accommodation.", 
"Epigenetic information includes heritable signals that modulate gene expression but are not encoded in the primary nucleotide sequence. We have studied natural epigenetic variation in three allotetraploid sibling orchid species (Dactylorhiza majalis s.str, D. traunsteineri s.l., and D. ebudensis) that differ radically in geography/ecology. The epigenetic variation released by genome doubling has been restructured in species-specific patterns that reflect their recent evolutionary history and have an impact on their ecology and evolution, hundreds of generations after their formation. Using two contrasting approaches that yielded largely congruent results, epigenome scans pinpointed epiloci under divergent selection that correlate with eco-environmental variables, mainly related to water availability and temperature. The stable epigenetic divergence in this group is largely responsible for persistent ecological differences, which then set the stage for species-specific genetic patterns to accumulate in response to further selection and/or drift. Our results strongly suggest a need to expand our current evolutionary framework to encompass a complementary epigenetic dimension when seeking to understand population processes that drive phenotypic evolution and adaptation.", 
"Genomics promises exciting advances towards the important conservation goal of maximizing evolutionary potential, notwithstanding associated challenges. Here, we explore some of the complexity of adaptation genetics and discuss the strengths and limitations of genomics as a tool for characterizing evolutionary potential in the context of conservation management. Many traits are polygenic and can be strongly influenced by minor differences in regulatory networks and by epigenetic variation not visible in DNA sequence. Much of this critical complexity is difficult to detect using methods commonly used to identify adaptive variation, and this needs appropriate consideration when planning genomic screens, and when basing management decisions on genomic data. When the genomic basis of adaptation and future threats are well understood, it may be appropriate to focus management on particular adaptive traits. For more typical conservations scenarios, we argue that screening genome-wide variation should be a sensible approach that may provide a generalized measure of evolutionary potential that accounts for the contributions of small-effect loci and cryptic variation and is robust to uncertainty about future change and required adaptive response(s). The best conservation outcomes should be achieved when genomic estimates of evolutionary potential are used within an adaptive management framework.", 
"Heritable phenotypic variation in plants can be caused not only by underlying genetic differences, but also by variation in epigenetic modifications such as DNA methylation. However, we still know very little about how relevant such epigenetic variation is to the ecology and evolution of natural populations. We conducted a greenhouse experiment in which we treated a set of natural genotypes of Arabidopsis thaliana with the demethylating agent 5-azacytidine and examined the consequences of this treatment for plant traits and their phenotypic plasticity. Experimental demethylation strongly reduced the growth and fitness of plants and delayed their flowering, but the degree of this response varied significantly among genotypes. Differences in genotypes' responses to demethylation were only weakly related to their genetic relatedness, which is consistent with the idea that natural epigenetic variation is independent of genetic variation. Demethylation also altered patterns of phenotypic plasticity, as well as the amount of phenotypic variation observed among plant individuals and genotype means. We have demonstrated that epigenetic variation can have a dramatic impact on ecologically important plant traits and their variability, as well as on the fitness of plants and their ecological interactions. Epigenetic variation may thus be an overlooked factor in the evolutionary ecology of plant populations.", 
"Although there is keen interest in the potential adaptive value of epigenetic variation, it is unclear what conditions favor the stability of these variants either within or across generations. Because epigenetic modifications can be environmentally sensitive, existing theory on adaptive phenotypic plasticity provides relevant insights. Our consideration of this theory suggests that stable maintenance of environmentally induced epigenetic states over an organism's lifetime is most likely to be favored when the organism accurately responds to a single environmental change that subsequently remains constant, or when the environmental change cues an irreversible developmental transition. Stable transmission of adaptive epigenetic states from parents to offspring may be selectively favored when environments vary across generations and the parental environment predicts the offspring environment. The adaptive value of stability beyond a single generation of parent-offspring transmission likely depends on the costs of epigenetic resetting. Epigenetic stability both within and across generations will also depend on the degree and predictability of environmental variation, dispersal patterns, and the (epi)genetic architecture underlying phenotypic responses to environment. We also discuss conditions that favor stability of random epigenetic variants within the context of bet hedging. We conclude by proposing research directions to clarify the adaptive significance of epigenetic stability.", 
"The role that epigenetic inheritance can play in adaptation may differ between sexuals and asexuals because (1) the dynamics of adaptation differ under sexual and asexual reproduction and the opportunities offered by epigenetic inheritance may affect these dynamics differently; and (2) in asexual reproduction epigenetic reprogramming mechanisms that are associated with meiosis can be bypassed, which could promote the buildup of epigenetic variation in asexuals. Here, we evaluate current evidence for an epigenetic contribution to adaptation in asexuals. We argue that two aspects of epigenetic variation should have particular relevance for asexuals, namely epigenetics-mediated phenotypic plasticity within and between generations, and heritable variation via stochastic epimutations. An evaluation of epigenetic reprogramming mechanisms suggests that some, but not all, forms of asexual reproduction enhance the likelihood of stable transmission of epigenetic marks across generations compared to sexual reproduction. However, direct tests of these predicted sexual-asexual differences are virtually lacking. Stable transmission of DNA methylation, transcriptomes, and phenotypes from parent to clonal offspring are demonstrated in various asexual species, and clonal genotypes from natural populations show habitat-specific DNA methylation. We discuss how these initial observations can be extended to demonstrate an epigenetic contribution to adaptation.", 
"Individual variation in ecologically important features of organisms is a crucial element in ecology and evolution, yet disentangling its underlying causes is difficult in natural populations. We applied a genomic scan approach using amplified fragment length polymorphism (AFLP) markers to quantify the genetic basis of long-term individual differences in herbivory by mammals at a wild population of the violet Viola cazorlensis monitored for two decades. In addition, methylation-sensitive amplified polymorphism (MSAP) analyses were used to investigate the association between browsing damage and epigenetic characteristics of individuals, an aspect that has been not previously explored for any wild plant. Structural equation modelling was used to identify likely causal structures linking genotypes, epigenotypes and herbivory. Individuals of V. cazorlensis differed widely in the incidence of browsing mammals over the 20-year study period. Six AFLP markers (1.6% of total) were significantly related to herbivory, accounting altogether for 44% of population-wide variance in herbivory levels. MSAP analyses revealed considerable epigenetic variation among individuals, and differential browsing damage was significantly related to variation in multilocus epigenotypes. In addition, variation across plants in epigenetic characteristics was related to variation in several herbivory-related AFLP markers. Statistical comparison of alternative causal models suggested that individual differences in herbivory are the outcome of a complex causal structure where genotypes and epigenotypes are interconnected and have direct and indirect effects on herbivory. Insofar as methylation states of MSAP markers influential on herbivory are transgenerationally heritable, herbivore-driven evolutionary changes at the study population will involve correlated changes in genotypic and epigenotypic distributions.", 
"Because the maintenance of proper developmental temperatures during avian incubation is costly to parents, embryos of many species experience pronounced variation in incubation temperature. However, the effects of such temperature variation on nestling development remain relatively unexplored. To investigate this, we artificially incubated wild blue tit (Cyanistes caeruleus L.) clutches at 35.0 degrees, 36.5 degrees, or 38.0 degrees C for two-thirds of the incubation period. We returned clutches to their original nests before hatching and subsequently recorded nestling growth and resting metabolic rate. The length of the incubation period decreased with temperature, whereas hatching success increased. Nestlings from the lowest incubation temperature group had shorter tarsus lengths at 2 weeks of age, but body mass and wing length were not affected by temperature. In addition, nestlings from the lowest temperature group had a significantly higher resting metabolic rate compared with mid- and high-temperature nestlings, which may partly explain observed size differences between the groups. These findings suggest that nest microclimate can influence nestling phenotype, but whether observed differences carry over to later life-history stages remains unknown.", 
"Epigenetic mechanisms are proposed as an important way in which the genome responds to the environment. Epigenetic marks, including DNA methylation and Histone modifications, can be triggered by environmental effects, and lead to permanent changes in gene expression, affecting the phenotype of an organism. Epigenetic mechanisms have been proposed as key in plasticity, allowing environmental exposure to shape future gene expression. While we are beginning to understand how these mechanisms have roles in human biology and disease, we have little understanding of their roles and impacts on ecology and evolution. In this review, we discuss different types of epigenetic marks, their roles in gene expression and plasticity, methods for assaying epigenetic changes, and point out the future advances we require to understand fully the impact of this field. J. Exp. Zool. (Mol. Dev. Evol.) 322B: 208-220, 2014. (c) 2014 Wiley Periodicals, Inc.", 
"Transposable elements (TEs) are a dominant feature of most flowering plant genomes. Together with other accepted facilitators of evolution, accumulating data indicate that TEs can explain much about their rapid evolution and diversification. Genome size in angiosperms is highly correlated with TE content and the overwhelming bulk (> 80%) of large genomes can be composed of TEs. Among retro-TEs, long terminal repeats (LTRs) are abundant, whereas DNA-TEs, which are often less abundant than retro-TEs, are more active. Much adaptive or evolutionary potential in angiosperms is due to the activity of TEs (active TE-Thrust), resulting in an extraordinary array of genetic changes, including gene modifications, duplications, altered expression patterns, and exaptation to create novel genes, with occasional gene disruption. TEs implicated in the earliest origins of the angiosperms include the exapted Mustang, Sleeper, and Fhy3/Far1 gene families. Passive TE-Thrust can create a high degree of adaptive or evolutionary potential by engendering ectopic recombination events resulting in deletions, duplications, and karyotypic changes. TE activity can also alter epigenetic patterning, including that governing endosperm development, thus promoting reproductive isolation. Continuing evolution of long-lived resprouter angiosperms, together with genetic variation in their multiple meristems, indicates that TEs can facilitate somatic evolution in addition to germ line evolution. Critical to their success, angiosperms have a high frequency of polyploidy and hybridization, with resultant increased TE activity and introgression, and beneficial gene duplication. Together with traditional explanations, the enhanced genomic plasticity facilitated by TE-Thrust, suggests a more complete and satisfactory explanation for Darwin's abominable mystery: the spectacular success of the angiosperms.", 
"DNA methylation is an important, heritable epigenetic modification in most eukaryotic organisms that is connected with numerous biological processes. To study the impact of natural epigenetic variation in an ecological or evolutionary context, epigenetic studies are increasingly using methylation-sensitive amplification polymorphism (MSAP) for surveys at the population or species level. However, no consensus exists on how to interpret and score the multistate information obtained from the MSAP banding patterns. Here, we review the previously used scoring approaches for population epigenetic studies and develop new alternatives. To assess effects of the different approaches on parameters of epigenetic diversity and differentiation, we applied eight scoring schemes to a case study of three populations of the plant species Viola elatior. For a total number of 168 detected polymorphic MSAP fragments, the number of ultimately scored polymorphic epiloci ranged between 78 and 286 depending on the particular scoring scheme. Both, estimates of epigenetic diversity and differentiation varied strongly between scoring approaches. However, linear regression and PCoA revealed qualitatively similar patterns, suggesting that the scoring approaches are largely consistent. For single-locus analyses of MSAP data, for example the search for loci under selection, we advocate a new scoring approach that separately takes into account different methylation types and thus seems appropriate for drawing more detailed conclusions in ecological or evolutionary contexts. An R script (MSAP_score.r) for scoring and basic data analysis is provided.", 
"Karten's neocortex hypothesis holds that many component cell populations of the sauropsid dorsal ventricular ridge (DVR) are homologous to particular cell populations in layers of auditory and visual tectofugal-recipient neocortex of mammals (i.e., temporal neocortex), as well as to some amygdaloid populations. The claustroamygdalar hypothesis, based on gene expression domains, proposes that mammalian homologues of DVR are found in the claustrum, endopiriform nuclei, and/or pallial amygdala. Because hypotheses of homology need to account for the totality of the evidence, the available data on multiple forebrain features of sauropsids and mammals are reviewed here. While some genetic data are compatible with the claustroamygdalar hypothesis, and developmental (epigenetic) data are indecisive, hodological, morphological, and topographical data favor the neocortex hypothesis and are inconsistent with the claustroamygdalar hypothesis. Detailed studies of gene signaling cascades that establish neuronal cell-type identity in DVR, tectofugal-recipient neocortex, and claustroamygdala will be needed to resolve this debate about the evolution of neocortex.", 
"Maternal effects are now universally recognised as a form of nongenetic. parental influence on offspring but, until recently, paternal effects were regarded as an anomaly. Although it is now clear that paternal effects are both widespread and important, their proximate basis and evolutionary consequences have received little attention and remain poorly understood. In particular, because many paternal effects are mediated by maternal responses such as differential allocation, the boundary between paternal and maternal effects is sometimes blurred. We distinguish here three basic types of paternal effect and clarify the role of maternal responses in these effects. We also outline key questions that can serve as a road map for research on the proximate basis and evolutionary implications of paternal effects.", 
"There is increasing evidence for epigenetically mediated transgenerational inheritance across taxa. However, the evolutionary implications of such alternative mechanisms of inheritance remain unclear. Herein, we show that epigenetic mechanisms can serve two fundamentally different functions in transgenerational inheritance: (i) selection-based effects, which carry adaptive information in virtue of selection over many generations of reliable transmission; and (ii) detection-based effects, which are a transgenerational form of adaptive phenotypic plasticity. The two functions interact differently with a third form of epigenetic information transmission, namely information about cell state transmitted for somatic cell heredity in multicellular organisms. Selection-based epigenetic information is more likely to conflict with somatic cell inheritance than is detection-based epigenetic information. Consequently, the evolutionary implications of epigenetic mechanisms are different for unicellular and multicellular organisms, which underscores the conceptual and empirical importance of distinguishing between these two different forms of transgenerational epigenetic effect.", 
"A dramatic rise in obesity has occurred among humans within the last several decades. Little is known about whether similar increases in obesity have occurred in animals inhabiting human-influenced environments. We examined samples collectively consisting of over 20 000 animals from 24 populations (12 divided separately into males and females) of animals representing eight species living with or around humans in industrialized societies. In all populations, the estimated coefficient for the trend of body weight over time was positive (i.e. increasing). The probability of all trends being in the same direction by chance is 1.2 x 10(-7). Surprisingly, we find that over the past several decades, average mid-life body weights have risen among primates and rodents living in research colonies, as well as among feral rodents and domestic dogs and cats. The consistency of these findings among animals living in varying environments, suggests the intriguing possibility that the aetiology of increasing body weight may involve several as-of-yet unidentified and/or poorly understood factors (e.g. viral pathogens, epigenetic factors). This finding may eventually enhance the discovery and fuller elucidation of other factors that have contributed to the recent rise in obesity rates.", 
"Retrotransposable elements comprise around 50% of the mammalian genome. Their activity represents a constant threat to the host and has prompted the development of adaptive control mechanisms to protect genome architecture and function. To ensure their propagation, retrotransposons have to mobilize in cells destined for the next generation. Accordingly, these elements are particularly well suited to transcriptional networks associated with pluripotent and germinal states in mammals. The relaxation of epigenetic control that occurs in the early developing germline constitutes a dangerous window in which retrotransposons can escape from host restraint and massively expand. What could be observed as risky behavior may turn out to be an insidious strategy developed by germ cells to sense retrotransposons and hold them back in check. Herein, we review recent insights that have provided a detailed picture of the defense mechanisms that concur toward retrotransposon silencing in mammalian genomes, and in particular in the germline. In this lineage, retrotransposons are hit at multiple stages of their life cycle, through transcriptional repression, RNA degradation and translational control. An organized cross-talk between PIWI-interacting small RNAs (piRNAs) and various nuclear and cytoplasmic accessories provides this potent and multilayered response to retrotransposon unleashing in early germ cells. Heredity (2010) 105, 92-104; doi:10.1038/hdy.2010.53; published online 5 May 2010", 
"Chromosomal sex determination systems create the opportunity for the evolution of selfish genetic elements that increase the transmission of one sex chromosome at the expense of its homolog. Because such selfish elements on sex chromosomes can reduce fertility and distort the sex ratio of progeny, unlinked suppressors are expected to evolve, bringing different regions of the genome into conflict over the meiotic transmission of the sex chromosomes. Here we argue that recurrent genetic conflict over sex chromosome transmission is an important evolutionary force that has shaped a wide range of seemingly disparate phenomena including the epigenetic regulation of genes expressed in the germline, the distribution of genes in the genome, and the evolution of hybrid sterility between species.", 
"In this study msap, an R package which analyses methylation-sensitive amplified polymorphism (MSAP or MS-AFLP) data is presented. The program provides a deep analysis of epigenetic variation starting from a binary data matrix indicating the banding pattern between the isoesquizomeric endonucleases HpaII and MspI, with differential sensitivity to cytosine methylation. After comparing the restriction fragments, the program determines if each fragment is susceptible to methylation (representative of epigenetic variation) or if there is no evidence of methylation (representative of genetic variation). The package provides, in a user-friendly command line interface, a pipeline of different analyses of the variation (genetic and epigenetic) among user-defined groups of samples, as well as the classification of the methylation occurrences in those groups. Statistical testing provides support to the analyses. A comprehensive report of the analyses and several useful plots could help researchers to assess the epigenetic and genetic variation in their MSAP experiments. msap is downloadable from CRAN (http://cran.r-project.org/) and its own webpage (http://msap.r-forge.R-project.org/). The package is intended to be easy to use even for those people unfamiliar with the R command line environment. Advanced users may take advantage of the available source code to adapt msap to more complex analyses.", 
"In this paper we describe a novel approach that may shed light on the genomic DNA methylation of organisms with non-resolved genomes. The LUminometric Methylation Assay (LUMA) is permissive for genomic DNA methylation studies of any genome as it relies on the use of methyl-sensitive and -insensitive restriction enzymes followed by polymerase extension via Pyrosequencing technology. Here, LUMA was used to characterize genomic DNA methylation in the lower brain stem region from 47 polar bears subsistence hunted in central East Greenland between 1999 and 2001. In these samples, average genomic DNA methylation was 57.9% +/- 6.69 (SD; range was 42.0 to 72.4%). When genomic DNA methylation was related to brain mercury (Hg) exposure levels, an inverse association was seen between these two variables for the entire study population (P for trend = 0.17). After dichotomizing animals by gender and controlling for age, a negative trend was seen amongst male animals (P for trend = 0.07) but no associations were found in female bears. Such sexually dimorphic responses have been found in other toxicological studies. Our results show that genomic DNA methylation can be quantitatively studied in a highly reproducible manner in tissue samples from a wild organism with a non-resolved genome. As such, LUMA holds great promise as a novel method to explore consequential questions across the ecological sciences that may require an epigenetic understanding.", 
"In addition to genetic differences between individuals as a result of nucleotide sequence variation, epigenetic changes that occur as a result of DNA methylation may also contribute to population niche width by enhancing phenotypic plasticity, although this intriguing possibility remains essentially untested. Using the nectar-living yeast Metschnikowia reukaufii as study subject, we examine the hypothesis that changes in genome-wide DNA methylation patterns underlie the ability of this fugitive species to exploit a broad resource range in its heterogeneous and patchy environment. Data on floral nectar characteristics and their use by M. reukaufii in the wild were combined with laboratory experiments and methylation-sensitive amplified polymorphism (MSAP) analyses designed to detect epigenetic responses of single genotypes to variations in sugar environment that mimicked those occurring naturally in nectar. M. reukaufii exploited a broad range of resources, occurring in nectar of 48% of species and 52% of families surveyed, and its host plants exhibited broad intra- and interspecific variation in sugar-related nectar features. Under experimental conditions, sugar composition, sugar concentration and their interaction significantly influenced the mean probability of MSAP markers experiencing a transition from unmethylated to methylated state. Alterations in methylation status were not random but predictably associated with certain markers. The methylation inhibitor 5-azacytidine (5-AzaC) had strong inhibitory effects on M. reukaufii proliferation in sugar-containing media, and a direct relationship existed across sugar X concentration experimental levels linking inhibitory effect of 5-AzaC and mean per-marker probability of genome-wide methylation. Environmentally induced DNA methylation polymorphisms allowed genotypes to grow successfully in extreme sugar environments, and the broad population niche width of M. reukaufii was largely made possible by epigenetic changes enabling genotype plasticity in resource use.", 
"Long terminal repeat-retrotransposons (LTR-RTs) are the most abundant class of transposable elements (TEs) in plants. They strongly impact the structure, function, and evolution of their host genome, and, in particular, their role in genome size variation has been clearly established. However, the dynamics of the process through which LTR-RTs have differentially shaped plant genomes is still poorly understood because of a lack of comparative studies. Using a new robust and automated family classification procedure, we exhaustively characterized the LTR-RTs in eight plant genomes for which a high-quality sequence is available (i.e., Arabidopsis thaliana, A. lyrata, grapevine, soybean, rice, Brachypodium dystachion, sorghum, and maize). This allowed us to perform a comparative genome-wide study of the retrotranspositional landscape in these eight plant lineages from both monocots and dicots. We show that retrotransposition has recurrently occurred in all plant genomes investigated, regardless their size, and through bursts, rather than a continuous process. Moreover, in each genome, only one or few LTR-RT families have been active in the recent past, and the difference in genome size among the species studied could thus mostly be accounted for by the extent of the latest transpositional burst(s). Following these bursts, LTR-RTs are efficiently eliminated from their host genomes through recombination and deletion, but we show that the removal rate is not lineage specific. These new findings lead us to propose a new model of TE-driven genome evolution in plants.", 
"In recent years, a number of researchers have advocated extending the modern synthesis in evolutionary biology. One of the core arguments made in favour of an extension comes from work on soft inheritance systems, including transgenerational epigenetic effects, cultural transmission and niche construction. In this study, we outline this claim and then take issue with it. We argue that the focus on soft inheritance has led to a conflation of proximate and ultimate causation, which has in turn obscured key questions about biological organization and calibration across the life span to maximize average lifetime inclusive fitness. We illustrate this by presenting hypotheses that we believe incorporate the core phenomena of soft inheritance and will aid in understanding them.", 
"Background: The Poly(ADP-ribose) polymerase (PARP) superfamily was originally identified as enzymes that catalyze the attachment of ADP-ribose subunits to target proteins using NAD+ as a substrate. The family is characterized by the catalytic site, termed the PARP signature. While these proteins can be found in a range of eukaryotes, they have been best studied in mammals. In these organisms, PARPs have key functions in DNA repair, genome integrity and epigenetic regulation. More recently it has been found that proteins within the PARP superfamily have altered catalytic sites, and have mono(ADP-ribose) transferase (mART) activity or are enzymatically inactive. These findings suggest that the PARP signature has a broader range of functions that initially predicted. In this study, we investigate the evolutionary history of PARP genes across the eukaryotes. Results: We identified in silico 236 PARP proteins from 77 species across five of the six eukaryotic supergroups. We performed extensive phylogenetic analyses of the identified PARPs. They are found in all eukaryotic supergroups for which sequence is available, but some individual lineages within supergroups have independently lost these genes. The PARP superfamily can be subdivided into six clades. Two of these clades were likely found in the last common eukaryotic ancestor. In addition, we have identified PARPs in organisms in which they have not previously been described. Conclusions: Three main conclusions can be drawn from our study. First, the broad distribution and pattern of representation of PARP genes indicates that the ancestor of all extant eukaryotes encoded proteins of this type. Second, the ancestral PARP proteins had different functions and activities. One of these proteins was similar to human PARP1 and likely functioned in DNA damage response. The second of the ancestral PARPs had already evolved differences in its catalytic domain that suggest that these proteins may not have possessed poly(ADP-ribosyl)ation activity. Third, the diversity of the PARP superfamily is larger than previously documented, suggesting as more eukaryotic genomes become available, this gene family will grow in both number and type.", 
"Male rats (Rattus novergicus) infected with protozoan Toxoplasma gondii relinquish their innate aversion to the cat odours. This behavioural change is postulated to increase transmission of the parasite to its definitive felid hosts. Here, we show that the Toxoplasma gondii infection institutes an epigenetic change in the DNA methylation of the arginine vasopressin promoter in the medial amygdala of male rats. Infected animals exhibit hypomethylation of arginine vasopressin promoter, leading to greater expression of this nonapeptide. The infection also results in the greater activation of the vasopressinergic neurons after exposure to the cat odour. Furthermore, we show that loss of fear in the infected animals can be rescued by the systemic hypermethylation and recapitulated by directed hypomethylation in the medial amygdala. These results demonstrate an epigenetic proximate mechanism underlying the extended phenotype in the Rattus novergicus-Toxoplasma gondii association. See also the Perspective by Jaroslav Flegr", 
"Selection for enhanced cognitive traits is hypothesized to produce enhancements to brain structures that support those traits. Although numerous studies suggest that this pattern is robust, there are several mechanisms that may produce this association. First, cognitive traits and their neural underpinnings may be fixed as a result of differential selection on cognitive function within specific environments. Second, these relationships may be the product of the selection for plasticity, where differences are produced owing to an individual's experiences in the environment. Alternatively, the relationship may be a complex function of experience, genetics and/or epigenetic effects. Using a well-studied model species (black-capped chickadee, Poecile atricapillus), we have for the first time, to our knowledge, addressed these hypotheses. We found that differences in hippocampal (Hp) neuron number, neurogenesis and spatial memory previously observed in wild chickadees persisted in hand-raised birds from the same populations, even when birds were raised in an identical environment. These findings reject the hypothesis that variation in these traits is owing solely to differences in memory-based experiences in different environments. Moreover, neuron number and neurogenesis were strikingly similar between captive-raised and wild birds from the same populations, further supporting the genetic hypothesis. Hp volume, however, did not differ between the captive-raised populations, yet was very different in their wild counterparts, supporting the experience hypothesis. Our results indicate that the production of some Hp factors may be inherited and largely independent of environmental experiences in adult life, regardless of their magnitude, in animals under high selection pressure for memory, while traits such as volume may be more plastic and modified by the environment.", 
"Early-life stress caused by the deprivation of maternal care has been shown to have long-lasting effects on the hypothalamic-pituitary-adrenal (HPA) axis in offspring of uniparental mammalian species. We asked if deprivation of maternal care in biparental species alters stress responsiveness of offspring, using a biparental avian species-the zebra finch, Taeniopygia guttata. In our experiment, one group of birds was raised by both male and female parents (control), and another was raised by males alone (maternally deprived). During adulthood, offspring of both groups were subjected to two stressors (restraint and isolation), and corticosterone concentrations were measured. Additionally, we measured baseline levels of the two corticosteroid receptors-glucocorticoid receptor (GR) and mineralocorticoid receptor (MR)-in the hippocampus, hypothalamus and cerebellum. Our results suggest that maternally deprived offspring are hyper-responsive to isolation in comparison with controls. Furthermore, mRNA levels of both GR and MR receptors are altered in maternally deprived offspring in comparison with controls. Thus, absence of maternal care has lasting consequences for HPA function in a biparental species where paternal care is available.", 
"DNA methylation is an epigenetic mechanism that has the potential to affect plant phenotypes and that is responsive to environmental and genomic stresses such as hybridization and polyploidization. We explored de novo methylation variation that arises during the formation of triploid asexual dandelions from diploid sexual mother plants using methylation-sensitive amplified fragment length polymorphism (MS-AFLP) analysis. In dandelions, triploid apomictic asexuals are produced from diploid sexual mothers that are fertilized by polyploid pollen donors. We asked whether the ploidy level change that accompanies the formation of new asexual lineages triggers methylation changes that contribute to heritable epigenetic variation within novel asexual lineages. Comparison of MS-AFLP and AFLP fragment inheritance in a diploid x triploid cross revealed de novo methylation variation between triploid F(1) individuals. Genetically identical offspring of asexual F(1) plants showed modest levels of methylation variation, comparable to background levels as observed among sibs in a long-established asexual lineage. Thus, the cross between ploidy levels triggered de novo methylation variation between asexual lineages, whereas it did not seem to contribute directly to variation within new asexual lineages. The observed background level of methylation variation suggests that considerable autonomous methylation variation could build up within asexual lineages under natural conditions.", 
"DNA methylation is a fundamental epigenetic mark known to have wide-ranging effects on gene regulation in a variety of animal taxa. Comparative genomic analyses can help elucidate the function of DNA methylation by identifying conserved features of methylated genes and other genomic regions. In this study, we used computational approaches to distinguish genes marked by heavy methylation from those marked by little or no methylation in the pea aphid, Acyrthosiphon pisum. We investigated if these two classes had distinct evolutionary histories and functional roles by conducting comparative analysis with the honeybee, Apis (Ap.) mellifera. We found that highly methylated orthologs in A. pisum and Ap. mellifera exhibited greater conservation of methylation status, suggesting that highly methylated genes in ancestral species may remain highly methylated over time. We also found that methylated genes tended to show different rates of evolution than unmethylated genes. In addition, genes targeted by methylation were enriched for particular biological processes that differed from those in relatively unmethylated genes. Finally, methylated genes were preferentially ubiquitously expressed among alternate phenotypes in both species, whereas genes lacking signatures of methylation were preferentially associated with condition-specific gene expression. Overall, our analyses support a conserved role for DNA methylation in insects with comparable methylation systems.", 
"The epigenetic phenomenon of genomic imprinting has motivated the development of numerous theories for its evolutionary origins and genomic distribution. In this review, we examine the three theories that have best withstood theoretical and empirical scrutiny. These are: Haig and colleagues' kinship theory; Day and Bonduriansky's sexual antagonism theory; and Wolf and Hager's maternal-offspring coadaptation theory. These theories have fundamentally different perspectives on the adaptive significance of imprinting. The kinship theory views imprinting as a mechanism to change gene dosage, with imprinting evolving because of the differential effect that gene dosage has on the fitness of matrilineal and patrilineal relatives. The sexual antagonism and maternal-offspring coadaptation theories view genomic imprinting as a mechanism to modify the resemblance of an individual to its two parents, with imprinting evolving to increase the probability of expressing the fitter of the two alleles at a locus. In an effort to stimulate further empirical work on the topic, we carefully detail the logic and assumptions of all three theories, clarify the specific predictions of each and suggest tests to discriminate between these alternative theories for why particular genes are imprinted.", 
"Inbreeding depression (i.e. negative fitness effects of inbreeding) is central in evolutionary biology, affecting numerous aspects of population dynamics and demography, such as the evolution of mating systems, dispersal behaviour and the genetics of quantitative traits. Inbreeding depression is commonly observed in animals and plants. Here, we demonstrate that, in addition to genetic processes, epigenetic processes may play an important role in causing inbreeding effects. We compared epigenetic markers of outbred and inbred offspring of the perennial plant Scabiosa columbaria and found that inbreeding increases DNA methylation. Moreover, we found that inbreeding depression disappears when epigenetic variation is modified by treatment with a demethylation agent, linking inbreeding depression firmly to epigenetic variation. Our results suggest an as yet unknown mechanism for inbreeding effects and demonstrate the importance of evaluating the role of epigenetic processes in inbreeding depression.", 
"Age is a fundamental aspect of animal ecology, but is difficult to determine in many species. Humpback whales exemplify this as they have a lifespan comparable to humans, mature sexually as early as 4 years and have no reliable visual age indicators after their first year. Current methods for estimating humpback age cannot be applied to all individuals and populations. Assays for human age have recently been developed based on age-induced changes in DNA methylation of specific genes. We used information on age-associated DNA methylation in human and mouse genes to identify homologous gene regions in humpbacks. Humpback skin samples were obtained from individuals with a known year of birth and employed to calibrate relationships between cytosine methylation and age. Seven of 37 cytosines assayed for methylation level in humpback skin had significant age-related profiles. The three most age-informative cytosine markers were selected for a humpback epigenetic age assay. The assay has an R-2 of 0.787 (P = 3.04e-16) and predicts age from skin samples with a standard deviation of 2.991 years. The epigenetic method correctly determined which of parent-offspring pairs is the parent in more than 93% of cases. To demonstrate the potential of this technique, we constructed the first modern age profile of humpback whales off eastern Australia and compared the results to population structure 5 decades earlier. This is the first epigenetic age estimation method for a wild animal species and the approach we took for developing it can be applied to many other non-model organisms.", 
"DNA methylation is an epigenetic mark that has key roles in the control of genome activity in plants and mammals. It is critical for the stable silencing of repeat elements and is also involved in the epigenetic regulation of some genes. Despite similarities in the controlling functions of DNA methylation, its dynamics and deposition patterns differ in several respects between plants and mammals. One of the most striking differences is that plants tend to propagate pre-existing DNA methylation states across generations, whereas mammals re-establish them genome wide at every generation. Here, we review our current understanding of DNA methylation in the flowering plant Arabidopsis. We discuss in particular the role of RNAi in the incremental methylation and silencing of repeat elements over successive generations. We argue that para-mutation, an epigenetic phenomenon first described in maize, is an extreme manifestation of this RNAi-dependent pathway. Heredity (2010) 105, 14-23; doi:10.1038/hdy.2010.52; published online 12 May 2010", 
"The functional and evolutionary significance of DNA methylation in insect genomes remains to be resolved. Nasonia is well situated for comparative analyses of DNA methylation and genome evolution, since the genomes of a moderately distant outgroup species as well as closely related sibling species are available. Using direct sequencing of bisulfite-converted DNA, we uncovered a substantial level of DNA methylation in 17 of 18 Nasonia vitripennis genes and a strong correlation between methylation level and CpG depletion. Notably, in the sex-determining locus transformer, the exon that is alternatively spliced between the sexes is heavily methylated in both males and females, whereas other exons are only sparsely methylated. Orthologous genes of the honeybee and Nasonia show highly similar relative levels of CpG depletion, despite similar to 190 My divergence. Densely and sparsely methylated genes in these species also exhibit similar functional enrichments. We found that the degree of CpG depletion is negatively correlated with substitution rates between closely related Nasonia species for synonymous, nonsynonymous, and intron sites. This suggests that mutation rates increase with decreasing levels of germ line methylation. Thus, DNA methylation is prevalent in the Nasonia genome, may participate in regulatory processes such as sex determination and alternative splicing, and is correlated with several aspects of genome and sequence evolution.", 
"Over the last four decades, bioarchaeology has experienced significant technical growth and theoretical maturation. Early 21st century bioarchaeology may also be enhanced from a renewed engagement with the concept of biological stress. New insights on biological stress and disease can be gained from cross-disciplinary perspectives regarding human skeletal variation and disease. First, pathophysiologic and molecular signaling mechanisms can provide more precise understandings regarding formation of pathological phenotypes in bone. Using periosteal new bone formation as an example, various mechanisms and pathways are explored in which new bone can be formed under conditions of biological stress, particularly in bone microenvironments that involve inflammatory changes. Second, insights from human biology are examined regarding some epigenetic factors and disease etiology. While epigenetic effects on stress and disease outcomes appear profoundly influential, they are mostly invisible in skeletal tissue. However, some indirect and downstream effects, such as the developmental origins of adult health outcomes, may be partially observable in bioarchaeological data. Emerging perspectives from the human microbiome are also considered. Microbiomics involves a remarkable potential to understand ancient biology, disease, and stress. Third, tools from epidemiology are examined that may aid bioarchaeologists to better cope with some of the inherent limitations of skeletal samples to better measure and quantify the expressions of skeletal stress markers. Such cross-disciplinary synergisms hopefully will promote more complete understandings of health and stress in bioarchaeological science. (C) 2014 Wiley Periodicals, Inc.", 
"An appreciation of the fundamental principles of evolutionary biology provides new insights into major diseases and enables an integrated understanding of human biology and medicine. However, there is a lack of awareness of their importance amongst physicians, medical researchers, and educators, all of whom tend to focus on the mechanistic (proximate) basis for disease, excluding consideration of evolutionary (ultimate) reasons. The key principles of evolutionary medicine are that selection acts on fitness, not health or longevity; that our evolutionary history does not cause disease, but rather impacts on our risk of disease in particular environments; and that we are now living in novel environments compared to those in which we evolved. We consider these evolutionary principles in conjunction with population genetics and describe several pathways by which evolutionary processes can affect disease risk. These perspectives provide a more cohesive framework for gaining insights into the determinants of health and disease. Coupled with complementary insights offered by advances in genomic, epigenetic, and developmental biology research, evolutionary perspectives offer an important addition to understanding disease. Further, there are a number of aspects of evolutionary medicine that can add considerably to studies in other domains of contemporary evolutionary studies.", 
"Variation of DNA methylation is thought to play an important role for rapid adjustments of plant populations to dynamic environmental conditions, thus compensating for the relatively slow response time of genetic adaptations. However, genetic and epigenetic variation of wild plant populations has not yet been directly compared in fast changing environments. Here, we surveyed populations of Viola elatior from two adjacent habitat types along a successional gradient characterized by strong differences in light availability. Using amplified fragment length polymorphisms (AFLP) and methylation-sensitive amplification polymorphisms (MSAP) analyses, we found relatively low levels of genetic (H-gen' = 0.19) and epigenetic (H-epi' = 0.23) diversity and high genetic (phi(ST) = 0.72) and epigenetic (phi(ST) = 0.51) population differentiation. Diversity and differentiation were significantly correlated, suggesting that epigenetic variation partly depends on the same driving forces as genetic variation. Correlation-based genome scans detected comparable levels of genetic (17.0%) and epigenetic (14.2%) outlier markers associated with site specific light availability. However, as revealed by separate differentiation-based genome scans for AFLP, only few genetic markers seemed to be actually under positive selection (0-4.5%). Moreover, principal coordinates analyses and Mantel tests showed that overall epigenetic variation was more closely related to habitat conditions, indicating that environmentally induced methylation changes may lead to convergence of populations experiencing similar habitat conditions and thus may play a major role for the transient and/or heritable adjustment to changing environments. Additionally, using a new MSAP-scoring approach, we found that mainly the unmethylated (phi(ST) = 0.60) and CG-methylated states (phi(ST) = 0.46) of epiloci contributed to population differentiation and putative habitat-related adaptation, whereas CHG-hemimethylated states (phi(ST) = 0.21) only played a marginal role.", 
"Epigenetic information is an important mediator of the relationship between genotype and phenotype in eukaryotic organisms. One of the most important and widely conserved forms of epigenetic information is the methylation of genes. However, the function of intragenic DNA methylation remains poorly understood. The goal of this study was to gain greater understanding of the nature of intragenic methylation by determining its role in the multilayered epigenetic landscape of insects. We first investigated the evolutionary lability of DNA methylation by examining whether methylation patterns were conserved in the fire ant and honey bee. We found that DNA methylation was targeted to largely overlapping sets of orthologs in both species. Next, we compared intragenic DNA methylation levels in the fire ant and honey bee to comprehensive epigenetic and gene-regulatory data from Drosophila melanogaster orthologs. We observed striking evidence of a conserved association between DNA methylation in fire ants and honey bees, and several active histone modifications, constitutive gene expression, and broad promoter architecture in D. melanogaster. Overall, our study illustrates that DNA methylation is a single component of a conserved, integrated, multilayered epigenetic and regulatory landscape in insect genomes.", 
"Modern evolutionary biology is founded on the Mendelian-genetic model of inheritance, but it is now clear that this model is incomplete. Empirical evidence shows that environment (encompassing all external influences on the genome) can impose transgenerational effects and generate heritable variation for a broad array of traits in animals, plants, and other organisms. Such effects can be mediated by the transmission of epigenetic, cytoplasmic, somatic, nutritional, environmental, and behavioral variation. Building on the work of many authors, we outline a general framework for conceptualizing nongenetic inheritance and its evolutionary implications. This framework shows that, by decoupling phenotypic change from the genotype, nongenetic inheritance can circumvent the limitations of genetic inheritance and thereby influence population dynamics and alter the fitness landscape. The weight of theory and empirical evidence indicates that nongenetic inheritance is a potent factor in evolution that can engender outcomes unanticipated under the Mendelian-genetic model.", 
"To study the consequences of hybridization and genome duplication on polyploid genome evolution and adaptation, we used independently formed hybrids (Spartina x townsendii and Spartina x neyrautii) that originated from natural crosses between Spartina alterniflora, an American introduced species, and the European native Spartina maritima. The hybrid from England, S. x townsendii, gave rise to the invasive allopolyploid, salt-marsh species, Spartina anglica. Recent studies indicated that allopolyploid speciation may be associated with rapid genetic and epigenetic changes. To assess this in Spartina, we performed AFLP (amplified fragment length polymorphism) and MSAP (methylation sensitive amplification polymorphism) on young hybrids and the allopolyploid. By comparing the subgenomes in the hybrids and the allopolyploid to the parental species, we inferred structural changes that arose repeatedly in the two independently formed hybrids. Surprisingly, 30% of the parental methylation patterns are altered in the hybrids and the allopolyploid. This high level of epigenetic regulation might explain the morphological plasticity of Spartina anglica and its larger ecological amplitude. Hybridization rather than genome doubling seems to have triggered most of the methylation changes observed in Spartina anglica.", 
"Phenotypic plasticity is the development of different phenotypes from a single genotype, depending on the environment. Such plasticity is a pervasive feature of life, is observed for various traits and is often argued to be the result of natural selection. A thorough study of phenotypic plasticity should thus include an ecological and an evolutionary perspective. Recent advances in large-scale gene expression technology make it possible to also study plasticity from a molecular perspective, and the addition of these data will help answer long-standing questions about this widespread phenomenon. In this review, we present examples of integrative studies that illustrate the molecular and cellular mechanisms underlying plastic traits, and show how new techniques will grow in importance in the study of these plastic molecular processes. These techniques include: (i) heterologous hybridization to DNA microarrays; (ii) next generation sequencing technologies applied to transcriptomics; (iii) techniques for studying the function of noncoding small RNAs; and (iv) proteomic tools. We also present recent studies on genetic model systems that uncover how environmental cues triggering different plastic responses are sensed and integrated by the organism. Finally, we describe recent work on changes in gene expression in response to an environmental cue that persist after the cue is removed. Such long-term responses are made possible by epigenetic molecular mechanisms, including DNA methylation. The results of these current studies help us outline future avenues for the study of plasticity.", 
"The Modern Synthesis (MS) is the current paradigm in evolutionary biology. It was actually built by expanding on the conceptual foundations laid out by its predecessors, Darwinism and neo-Darwinism. For sometime now there has been talk of a new Extended Evolutionary Synthesis (EES), and this article begins to outline why we may need such an extension, and how it may come about. As philosopher Karl Popper has noticed, the current evolutionary theory is a theory of genes, and we still lack a theory of forms. The field began, in fact, as a theory of forms in Darwin's days, and the major goal that an EES will aim for is a unification of our theories of genes and of forms. This may be achieved through an organic grafting of novel concepts onto the foundational structure of the MS, particularly evolvability, phenotypic plasticity, epigenetic inheritance, complexity theory, and the theory of evolution in highly dimensional adaptive landscapes.", 
"The genus Silene, studied by Darwin, Mendel and other early scientists, is re-emerging as a system for studying interrelated questions in ecology, evolution and developmental biology. These questions include sex chromosome evolution, epigenetic control of sex expression, genomic conflict and speciation. Its well-studied interactions with the pathogen Microbotryum has made Silene a model for the evolution and dynamics of disease in natural systems, and its interactions with herbivores have increased our understanding of multi-trophic ecological processes and the evolution of invasiveness. Molecular tools are now providing new approaches to many of these classical yet unresolved problems, and new progress is being made through combining phylogenetic, genomic and molecular evolutionary studies with ecological and phenotypic data. Heredity (2009) 103, 5-14; doi: 10.1038/hdy.2009.34; published online 15 April 2009", 
"Understanding the developmental and genetic basis for evolutionarily significant morphological variation in complex phenotypes such as the mammalian skull is a challenge because of the sheer complexity of the factors involved. We hypothesize that even in this complex system, the expression of phenotypic variation is structured by the interaction of a few key developmental processes. To test this hypothesis, we created a highly variable sample of crania using four mouse mutants and their wild-type controls from similar genetic backgrounds with developmental perturbations to particular cranial regions. Using geometric morphometric methods we compared patterns of size, shape, and integration in the sample within and between the basicranium, neurocranium, and face. The results highlight regular and predictable patterns of covariation among regions of the skull that presumably reflect the epigenetic influences of the genetic perturbations in the sample. Covariation between relative widths of adjoining regions is the most dominant factor, but there are other significant axes of covariation such as the relationship between neurocranial size and basicranial flexion. Although there are other sources of variation related to developmental perturbations not analyzed in this study, the patterns of covariation created by the epigenetic interactions evident in this sample may underlie larger scale evolutionary patterns in mammalian craniofacial form.", 
"Form and genes often tell different stories about the evolution of animals, with molecular data generally considered to be more objective than morphological data. However, form provides the basis for the description of organisms, and the study of fossils crucially depends on morphology. Complex organisms tend to evolve as 'mosaics', in which parts may be modified at varying rates and in response to different selective pressures. Thus, individual anatomical regions may contain different phylogenetic signals. In the present study, we used computerized methods to 'dissect' the skulls of a primate clade, the guenons, into functional and developmental modules (FDM). The potential of different modules as proxies for phylogenetic divergence in modern lineages was investigated. We found that the chondrocranium was the only FDM in which shape consistently had a strong and significant phylogenetic signal. This region might be less susceptible to epigenetic factors and thus more informative about phylogeny. The examination of the topology of trees from the chondrocranium suggested that the main differences evolved at the time of the radiation of terrestrial and arboreal guenons. However, phylogenetic reconstructions were found to be strongly affected by sampling error, with more localized anatomical regions (i.e. smaller/less complex FDMs) generally producing less reproducible tree topologies. This finding, if confirmed in other groups, implies that the utility of specific FDMs for phylogenetic inference could, in many cases, be hampered by the low reproducibility of results. The study also suggested that uncertainties due to sampling error may be larger than those from character sampling. This might have implications for phylogenetic analyses, which typically provide estimates of support of tree nodes based on characters but do not generally take into account the effect of sampling error on the tree topology. Nonetheless, studies of the potential of different FDMs as proxies for phylogenetic divergence in modern lineages, such as the present study, provide a framework that may help in modelling the morphological evolution of present and fossil species. (C) 2008 The Linnean Society of London.", 
"This article introduces a special issue on evolutionary innovation and morphological novelty, two interrelated themes that have received a remarkable increase of attention over the past few years. We begin with a discussion of the question of whether innovation and novelty represent distinct evolutionary problems that require a distinct conceptualization. We argue that the mechanisms of innovation and their phenotypic results-novelty-can only be properly addressed if they are distinguished from the standard evolutionary themes of variation and adaptation, and we present arguments for making such a distinction. We propose that origination, the first formation of biological structures, is another distinct problem of morphological evolution, and that together with innovation and novelty it constitutes a conceptual complex we call the innovation triad. We define a problem agenda of the triad, which separates the analysis of the initiating conditions from the mechanistic realization of innovation, and we discuss the theoretical problems that arise from treating innovation as distinct from variation. Further, we categorize the empirical approaches that address themes of the innovation triad in recognizing four major strands of research: the morphology and systematics program, the gene regulation program, the epigenetic program, and the theoretical biology program. We provide examples of each program, giving priority to contributions in the present issue. In conclusion, we observe that the innovation triad is one of the defining topics of EvoDevo research and may represent its most pertinent contribution to evolutionary theory. We point out that an inclusion of developmental systems properties into evolutionary theory represents a shift of explanatory emphasis from the external factors of natural selection to the internal dynamics of developmental systems, complementing adaptation with emergence, and contingency with inherency.", 
"Most bilaterians specify primordial germ cells (PGCs) during early embryogenesis using either inherited cytoplasmic germ line determinants (preformation) or induction of germ cell fate through signaling pathways (epigenesis). However, data from nonbilaterian animals suggest that ancestral metazoans may have specified germ cells very differently from most extant bilaterians. Cnidarians and sponges have been reported to generate germ cells continuously throughout reproductive life, but previous studies on members of these basal phyla have not examined embryonic germ cell origin. To try to define the embryonic origin of PGCs in the sea anemone Nematostella vectensis, we examined the expression of members of the vasa and nanos gene families, which are critical genes in bilaterian germ cell specification and development. We found that vasa and nanos family genes are expressed not only in presumptive PGCs late in embryonic development, but also in multiple somatic cell types during early embryogenesis. These results suggest one way in which preformation in germ cell development might have evolved from the ancestral epigenetic mechanism that was probably used by a metazoan ancestor.", 
"It is widely recognized that maternal phenotype can have important effects on offspring, but paternal phenotype is generally assumed to have no influence in animals lacking paternal care. Nonetheless, selection may favour the transfer of environmentally acquired condition to offspring from both parents. Using a split-brood, cross-generational laboratory design, we manipulated a key environmental determinant of condition - larval diet quality - of parents and their offspring in the fly Telostylinus angusticollis, in which there is no evidence of paternal provisioning. Parental diet did not affect offspring survival, but high-condition mothers produced larger eggs, and their offspring developed more rapidly when on a poor larval diet. Maternal condition had no effect on adult body size of offspring. By contrast, large, high-condition fathers produced larger offspring, and follow-up assays showed that this paternal effect can be sufficient to increase mating success of male offspring and fecundity of female offspring. Our findings suggest that both mothers and fathers transfer their condition to offspring, but with effects on different offspring traits. Moreover, our results suggest that paternal effects can be important even in species lacking conventional forms of paternal care. In such species, the transfer of paternal condition to offspring could contribute to indirect selection on female mate preferences.", 
"We describe a new hypothesis for the development of autism, that it is driven by imbalances in brain development involving enhanced effects of paternally expressed imprinted genes, deficits of effects from maternally expressed genes, or both. This hypothesis is supported by: (1) the strong genomic-imprinting component to the genetic and developmental mechanisms of autism, Angelman syndrome, Rett syndrome and Turner syndrome; (2) the core behavioural features of autism, such as self-focused behaviour, altered social interactions and language, and enhanced spatial and mechanistic cognition and abilities, and (3) the degree to which relevant brain functions and structures are altered in autism and related disorders. The imprinted brain theory of autism has important implications for understanding the genetic, epigenetic, neurological and cognitive bases of autism, as ultimately due to imbalances in the outcomes of intragenomic conflict between effects of maternally vs. paternally expressed genes.", 
"Mimulus guttatus (yellow monkeyflower) frequently produce glandular trichomes, a trait that may resist herbivory. Constitutive production of trichomes is variable both within and among populations of M. guttatus and most of this variation is genetic. This study demonstrates that damage on early leaves can induce increased trichome production on later leaves, a plastic response that is likely adaptive. Moreover, this study shows that this induction can be maternally transmitted, increasing trichome density in progeny before they experience herbivory. This transgenerational response must involve a yet undescribed epigenetic mechanism. These experiments also show genetic variation among plants in the capacity for both within and between plant generation induction. Despite the clear evolutionary importance of variation in constitutive and induced herbivory-resistance traits, few other studies have noted genetic variation in both within a plant species.", 
"The study of insect satellite DNAs (satDNAs) indicates the evolutionary conservation of certain features despite their sequence heterogeneity. Such features can include total length, monomer length, motifs, particular regions and/or secondary and tertiary structures. satDNAs may act as protein-binding sites, structural domains or sites for epigenetic modifications. The selective constraints in the evolution of satDNAs may be due to the satDNA sequence interaction with specific proteins important in heterochromatin formation and possible a role in controlling gene expression. The transcription of satDNA has been described in vertebrates, invertebrates and plants. In insects, differential satDNA expression has been observed in different cells, developmental stages, sex and caste of the individuals. These transcription differences may suggest their involvement in gene-regulation processes. In addition, the satDNA or its transcripts appear to be involved in heterochromatin formation and in chromatin-elimination processes. The importance of transposable elements to insect satDNA is shown by their presence as a constituent of satDNA in several species of insects (including possible active elements). In addition, they may be involved in the formation of centromeres and telomeres and in the homogenization and expansion of satDNA.", 
"Several models explain how a complex integrated system like the rodent mandible can arise from multiple developmental modules. The models propose various integrating mechanisms, including epigenetic effects of muscles on bones. We test five for their ability to predict correlations found in the individual (symmetric) and fluctuating asymmetric (FA) components of shape variation. We also use exploratory methods to discern patterns unanticipated by any model. Two models fit observed correlation matrices from both components: (1) parts originating in same mesenchymal condensation are integrated, (2) parts developmentally dependent on the same muscle form an integrated complex as do those dependent on teeth. Another fits the correlations observed in FA: each muscle insertion site is an integrated unit. However, no model fits well, and none predicts the complex structure found in the exploratory analyses, best described as a reticulated network. Furthermore, no model predicts the correlation between proximal parts of the condyloid and coronoid, which can exceed the correlations between proximal and distal parts of the same process. Additionally, no model predicts the correlation between molar alveolus and ramus and/or angular process, one of the highest correlations found in the FA component. That correlation contradicts the basic premise of all five developmental models, yet it should be anticipated from the epigenetic effects of mastication, possibly the primary morphogenetic process integrating the jaw coupling forces generated by muscle contraction with those experienced at teeth.", 
"Accumulating evidence suggests that hybrid genetic dysfunctions accrue not only because of sequence divergence of incompatible alleles but also result from a broad variety of mechanisms related to the maintenance of chromatin integrity. For example, it has been observed that hybridization in plants and mammals disrupts patterns of DNA methylation and imprinting. These epigenetic changes can be associated with transcriptional activation and mobilization of transposable elements in hybrids. It raises a question of how these alterations are matched by small regulatory RNAs, such as piwi-interacting RNAs, which play a potent role in both suppressing transposable elements and epigenetic control. The review offers a handful of glimpses into these complex dynamics.", 
"Molar microwear fabrics in extant mammals vary with diet and, more particularly, the physical properties of the items that are consumed. Praeanthropus afarensis is well represented in the fossil record over a prolonged and radiometrically controlled temporal span, and reasonably robust paleoecological reconstructions are available for the various localities from which it is known. We therefore examined molar microwear in this species to determine whether diet varied in relation to time or in response to different ecological conditions. Of more than 70 specimens of Pr. afarensis that contain one or more worn permanent molars, only 19 were found to be suitable for microwear analysis. These derive from eight temporal horizons in the Laetolil Beds and Hadar Formation spanning approximately 400 kyr (3.6-3.2 Ma). Six paleoecological categories have been reconstructed for these horizons, and these were ranked on the basis of floral cover. None of the microwear variables observed for Pr. afarensis is significantly associated with either temporal or paleoecological rank. Thus, microwear and, by extension, diet does not appear to have altered significantly in Pr. afarensis through time or in response to different paleoecological circumstances. The wear pattern that appears to have characterized Pr. afarensis overlaps extensively that of Gorilla gorilla beringei and differs notably from the fabrics of extant primates (e.g., Cebus apella and Cercocebus albigena) that consume hard objects. The high proportion of scratches on Pr. afarensis molars suggests the inclusion of fine abrasives in or on the food items consumed by those individuals sampled in this study. Although Pr. afarensis may have been morphologically equipped to process hard, brittle items, the microwear data suggest that it did not necessarily do so, even in the face of varying environmental circumstances. Explanatory scenarios that describe Pr. afarensis as part of an evolutionary trajectory involving a more heavily masticated diet with an increased reliance on hard, brittle items need to be reconsidered. However, fallback foods that were consumed during relatively short, albeit critical periods may have exerted sufficient selective pressure to explain the evolution of the comparatively robust Pr. afarensis trophic apparatus. Because it is unlikely that many individuals from such restricted temporal intervals would be sampled in the paleontological record, we suggest that the most productive approach to the elucidation of paleodiet is the integration of genetic (morphological) and epigenetic (microwear and isotopic) lines of evidence. (c) 2006 Elsevier Ltd. All rights reserved.", 
"Cytosine methylation is important in the epigenetic regulation of gene expression and development in plants and has been implicated in silencing duplicate genes after polyploid formation in several plant groups. Relatively little information exists, however, on levels and patterns of methylation polymorphism (MP) at homologous loci within species. Here we explored the levels and patterns of methylation-polymorphism diversity at CCGG sites within allotetraploid cotton, Gossypium hirsutum, using a methylation-sensitive amplified fragment length polymorphism screen and a selected set of 20 G. hirsutum accessions for which we have information on genetic polymorphism levels and relationships. Methylation and MP exist at high levels within G. hirsutum: of 150 HpaII/MspI sites surveyed, 48 were methylated at the inner cytosine (32%) and 32 of these were polymorphic (67%). Both these values are higher than comparable measures of genetic diversity using restriction fragment length polymorphisms. The high percentage of methylation-polymorphic sites and potential relationship to gene expression Underscore the potential significance of MP within and among populations. We speculate that biased correlation of methylation-polymorphic sites and genes in cotton may be a consequence of polyploidy and the attendant doubling of all genes.", 
"Hvbridization and polyploidization are now recognized as major phenomena in the evolution of plants, promoting,Q genetic diversity, adaptive radiation and speciation. Modern molecular techniques have recently provided evidence that allopolyploidy can induce several types of genetic and epigenetic events that are of critical importance for the evolutionary success of these plants: (1) chromosomal rearrangements within one or both parental genomes contribute toward proper meiotic pairing and isolation of the hybrid from its progenitors; (2) demethylation and activation of dormant transposable elements may trigger insertional mutagenesis and changes in local patterns of gene expression, facilitating rapid genomic reorganization; (3) rapid and reproducible loss of low copy DNA sequences appears to result in further differentiation of homoeologous chromosomes; and (4) organ-specific up- or down-regulation of one of the duplicated genes, may result in unequal expression or silencing one copy. All these alterations also have the potential, while stabilizing allopolyploid genomes, to produce novel expression patterns and new phenotypes, which together with increased heterozygosity and gene redundancy might confer on allopolyploids an elevated evolutionary potential, with effects at scales ranging from molecular to ecological. Although important advances have been rnade in understanding genomic responses to allopolyploidization, further insights are still expected to be gained in the near future, Such as the direction and nature of the diploidization process, functional relevance of gene expression alterations, molecular mechanisms that result in adaptation to different ecologies/habitats, and ecological and evolutionary implications of recurrent polyploidization.", 
"Planarians are highly regenerative organisms with the ability to remake all their cell types, including the germ cells. The germ cells have been suggested to arise from totipotent neoblasts through epigenetic mechanisms. Nanos is a zinc-finger protein with a widely conserved role in the maintenance of germ cell identity. In this work, we describe the expression of a planarian nanos-like gene Smednos in two kinds of precursor cells namely, primordial germ cells and eye precursor cells, during both development and regeneration of the planarian Schmidtea mediterranea. In sexual planarians, Smednos is expressed in presumptive male primordial germ cells of embryos from stage 8 of embryogenesis and throughout development of the male gonads and in the female primordial germ cells of the ovary. Thus, upon hatching, juvenile planarians do possess primordial germ cells. In the asexual strain, Smednos is expressed in presumptive male and female primordial germ cells. During regeneration, Smednos expression is maintained in the primordial germ cells, and new clusters of Smednos-positive cells appear in the regenerated tissue. Remarkably, during the final stages of development (stage 8 of embryogenesis) and during regeneration of the planarian eye, Smednos is expressed in cells surrounding the differentiating eye cells, possibly corresponding to eye precursor cells. Our results suggest that similar genetic mechanisms might be used to control the differentiation of precursor cells during development and regeneration in planarians.", 
"Ty3/gypsy retrotransposons are rare in mammalian genomes despite their abundance in invertebrate and other vertebrate classes. Here we identify a family of nine conserved mammalian genes with homology to Ty3/gypsy retrotransposons but which have lost their ability to autonomously retrotranspose. Of these, five map to the X chromosome while the remaining four are autosomal. Comparative phylogenetic analyses show them to have strongest homology to the sushi-ichi element from Fugu rubripes. Two of the autosomal gene members, Peg10 and Rtl1, are known to be imprinted, being expressed from the paternally inherited chromosome homologue. This suggests, consistent with the host-parasite response theory of the evolution of the imprinting mechanism, that parental-origin specific epigenetic control may be mediated by genomic parasitic elements such as these. Alternatively, these elements may preferentially integrate into regions that are differentially modified on the two homologous chromosomes such as imprinted domains and the X chromosome and acquire monoallelic expression. We assess the imprinting status of the remaining autosomal members of this family and show them to be biallelically expressed in embryo and placenta. Furthermore, the methylation status of Rtl1 was assayed throughout development and was found to resemble that of actively, silenced repetitive elements rather than imprinted sequences. This indicates that the ability to undergo genomic imprinting is not an inherent property of all members of this family of retroelements. Nonetheless, the conservation but functional divergence between the different members suggests that they have undergone positive selection and acquired distinct endogenous functions within their mammalian hosts.", 
"Human promoters divide into 2 classes, the low CpG (LCG) and the high CpG (HCG), based on their CpG dinucleotide content. The LCG class of promoters is hypermethylated and is associated with tissue-specific genes, whereas the HCG class is hypomethylated and associated with broadly expressed genes. By analyzing several chordate genomes separated for hundreds of millions of years, here we show that the divide between low CpG and high CpG promoters is conserved in several distantly related vertebrate taxa (including human, chicken, frog, lizard, and fish) but not in close invertebrate outgroups (sea squirts). Furthermore, LCG and HCG promoters are distinctively associated with tissue-specific and broadly expressed genes in these distantly related vertebrate taxa. Our results indicate that the function of DNA methylation on gene expression is conserved across these vertebrate taxa and suggest that the 2 classes of promoters have evolved early in vertebrate evolution, as a consequence of the advent of global DNA methylation.", 
"The vertebrate limb has provided evolutionary and developmental biologists with grist for theory and experiment for at least a century. Its most salient features are its pattern of discrete skeletal elements, the general proximodistal increase in element number as development proceeds, and the individualization of size and shape of the elements in line with functional requirements. Despite increased knowledge of molecular changes during limb development, however, the mechanisms for origination and innovation of the vertebrate limb pattern are still uncertain. We suggest that the bauplan of the limb is based on an interplay of genetic and epigenetic processes; in particular, the self-organizing properties of precartilage mesenchymal tissue are proposed to provide the basis for its ability to generate regularly spaced nodules and rods of cartilage. We provide an experimentally based core set of cellular and molecular processes in limb mesenchyme that, under realistic conditions, exhibit the requisite self-organizing behavior for pattern origination. We describe simulations that show that under limb bud-like geometries the core mechanism gives rise to skeletons with authentic proximodistal spatiotemporal organization. Finally, we propose that evolution refines skeletal templates generated by this process by mobilizing accessory molecular and biomechanical regulatory processes to shape the developing limb and its individual elements. Morphological innovation may take place when such modulatory processes exceed a threshold defined by the dynamics of the skeletogenic system and elements are added or lost.", 
"The mammalian mandible is a developmentally modular but functionally integrated system. Whether morphological integration can evolve to match the optimal pattern of functional integration may depend on the developmental origin of integration, specifically, on the role that direct epigenetic interactions play in shaping integration. These interactions are hypothesized to integrate modules and also to be highly conservative, potentially constraining the evolution of integration. Using the fox squirrel (Sciurus niger) mandible as a model system, we test five a priori developmental hypotheses that predict mandibular integration and we also explore for correlations between shapes of mandibular regions not anticipated by any of the developmental models. To determine whether direct epigenetic interactions are highly conserved in rodents, we examine the correlation structure of fluctuating asymmetry, and compare integration patterns between fox squirrels and prairie deer mice (Peromyscus maniculatus bairdii). In fox squirrels, we find a correlation structure unanticipated by all a priori developmental models: adjacent parts along the proximodistal jaw axis are correlated whereas more distant ones are not. The most notable exception is that the shape of the anterior incisor alveolus is correlated with the shape of the ramus (FA component) or coronoid (symmetric component). Those exceptions differ between species; in prairie deer mice, the molar alveolus is connected to more parts, and the incisor alveolus to fewer, than in fox squirrels. The structure of integration suggests that the mandible cannot be decomposed into parts but rather is a single connected unit, a result consistent with its functional integration. That match between functional and developmental integration may arise, at least in part, from function-induced growth, building developmental integration into the functional system and enabling direct epigenetic interactions to evolve when function does.", 
"Human reproductive ecology (HRE) is the study of the mechanisms that link variation in reproductive traits with variation in local habitats. Empirical and theoretical contributions from biological anthropology, physiology, and demography have established the foundation necessary for developing a comprehensive understanding, grounded in life history theory (LHT), of temporal, individual, and populational variation in women's reproductive functioning. LHT posits that natural selection leads to the evolution of mechanisms that tend to allocate resources to the competing demands of growth, reproduction, and survival such that fitness is locally maximized. (That is, among alternative allocation patterns exhibited in a population, those having the highest inclusive fitness will become more common over generational time.) Hence, strategic modulation of reproductive effort is potentially adaptive because investment in a new conception may risk one's own survival, future reproductive opportunities, and/or current offspring survival. The hypothalamic-pituitary-ovarian (HPO) axis is the principal neuroendocrine pathway by which the human female modulates reproductive functioning according to the changing conditions in her habitat. Adjustments of reproductive investment in a potential conception are manifested in temporal and individual variation in ovarian cycle length, ovulation, hormone levels, and the probability of conception. Understanding the extent and causes of adaptive and non-adaptive variation in ovarian functioning is fundamental to ascertaining the proximate and remote determinants of human reproductive patterns. In this review I consider what is known and what still needs to be learned of the ecology of women's reproductive biology, beginning with a discussion of the principal explanatory frameworks in HRE and the biometry of ovarian functioning. Turning next to empirical studies, it is evident that marked variation between cycles, women, and populations is the norm rather than an aberration. Other than woman's age, the determinants of these differences are not well characterized, although developmental conditions, dietary practices, genetic variation, and epigenetic mechanisms have all been hypothesized to play some role. It is also evident that the reproductive functioning of women born and living in arduous conditions is not analogous to that of athletes, dieters, or even the lower end of the normal range of HPO functioning in wealthier populations. Contrary to the presumption that humans have low fecundity and an inefficient reproductive system, both theory and present evidence suggest that we may actually have very high fecundity and a reproductive system that has evolved to be flexible, ruthlessly efficient and, most importantly, strategic. Yrbk Phys Anthropol 52:95-136, 2009. (C) 2009 Wiley-Liss, Inc.", 
"Background: The evolution of antibiotic resistance in bacteria is a topic of major medical importance. Evolution is the result of natural selection acting on variant phenotypes. Both the rigid base sequence of DNA and the more plastic expression patterns of the genes present define phenotype. Results: We investigated the evolution of resistant E. coli when exposed to low concentrations of antibiotic. We show that within an isogenic population there are heritable variations in gene expression patterns, providing phenotypic diversity for antibiotic selection to act on. We studied resistance to three different antibiotics, ampicillin, tetracycline and nalidixic acid, which act by inhibiting cell wall synthesis, protein synthesis and DNA synthesis, respectively. In each case survival rates were too high to be accounted for by spontaneous DNA mutation. In addition, resistance levels could be ramped higher by successive exposures to increasing antibiotic concentrations. Furthermore, reversion rates to antibiotic sensitivity were extremely high, generally over 50%, consistent with an epigenetic inheritance mode of resistance. The gene expression patterns of the antibiotic resistant E. coli were characterized with microarrays. Candidate genes, whose altered expression might confer survival, were tested by driving constitutive overexpression and determining antibiotic resistance. Three categories of resistance genes were identified. The endogenous beta-lactamase gene represented a cryptic gene, normally inactive, but when by chance expressed capable of providing potent ampicillin resistance. The glutamate decarboxylase gene, in contrast, is normally expressed, but when overexpressed has the incidental capacity to give an increase in ampicillin resistance. And the DAM methylase gene is capable of regulating the expression of other genes, including multidrug efflux pumps. Conclusion: In this report we describe the evolution of antibiotic resistance in bacteria mediated by the epigenetic inheritance of variant gene expression patterns. This provides proof in principle that epigenetic inheritance, as well as DNA mutation, can drive evolution.", 
"Many fungi have heterokaryotic life stages in which genetically different nuclei inhabit the same cell. In basidiomycetes, the heterokaryon is the product of mating and represents a genomic union very similar to a diploid thallus, yet the maintenance of unfused nuclei suggests a more complex association of the two genomes relative to diploidy. In species with variable numbers of nuclei per heterokaryotic cell, nuclear ratios within a mycelium may possibly become imbalanced (differ from 1:1) due to nuclear competition. In this study, heterokaryons of the basidiomycete Heterobasidion parviporum were examined to determine the effects of genotype and environment on nuclear ratios within vegetative mycelia. The data reveal that nuclear ratios are frequently imbalanced, generally stable over time, and genetically determined. The nuclear ratios were affected by environment, but the observed nuclear ratios did not follow the expectations of strong selection acting on a population of nuclei. Instead, these ratios were largely driven by genetic effects and epigenetic effects. Finally, the data suggest that nuclear ratio imbalance also affects both gene transcription and growth rate, implying that heterokaryotic basidiomycetes are not functionally equivalent to diploid individuals and have a higher potential for genotypic and phenotypic variation.", 
"Greater offspring predation favors evolution of faster development among species. We hypothesized that greater offspring predation exerts selection on mothers to increase levels of anabolic androgens in egg yolks to achieve faster development. Here, we tested whether (1) concentrations of yolk androgens in passerine species were associated with offspring predation and (2) embryo and nestling development rates were associated with yolk androgen concentrations. We examined three androgens that increase in potency along the synthesis pathway: androstenedione (A(4)) to testosterone (T) to 5 alpha-dihydrotestosterone (5 alpha-DHT). Concentrations of none of these steroids were related to clutch size; only A, was allometrically related to egg volume. Species that experience greater predation showed higher yolk concentrations of T and 5 alpha-DHT. Higher concentrations of T and particularly 5 alpha-DHT were strongly correlated with faster development during the embryo period and less so during the nestling period. Development rates were most strongly correlated with 5 alpha-DHT, suggesting that potency increases along the androgen synthesis pathway and that effects are mediated by the androgen receptor pathway. These results are consistent with the hypothesis that selection for faster development by time-dependent offspring mortality may be achieved epigenetically by varying embryo exposure to maternal anabolic steroids.", 
"Studies of microbial eukaryotes have been pivotal in the discovery of biological phenomena, including RNA editing, self-splicing RNA, and telomere addition. Here we extend this list by demonstrating that genome architecture, namely the extensive processing of somatic (macronuclear) genomes in some ciliate lineages, is associated with elevated rates of protein evolution. Using newly developed likelihood-based procedures for studying molecular evolution, we investigate 6 genes to compare 1) ciliate protein evolution to that of 3 other clades of eukaryotes (plants, animals, and fungi) and 2) protein evolution in ciliates with extensively processed macronuclear genomes to that of other ciliate lineages. In 5 of the 6 genes, ciliates are estimated to have a higher ratio of nonsynonymous/synonymous substitution rates, consistent with an increase in the rate of protein diversification in ciliates relative to other eukaryotes. Even more striking, there is a significant effect of genome architecture within ciliates as the most divergent proteins are consistently found in those lineages with the most highly processed macronuclear genomes. We propose a model whereby genome architecture-specifically chromosomal processing, amitosis within macronuclei, and epigenetics-allows ciliates to explore protein space in a novel manner. Further, we predict that examination of diverse eukaryotes will reveal additional evidence of the impact of genome architecture on molecular evolution.", 
"Gene duplication is a major force for generating evolutionary novelties that lead to adaptations to environments. We previously identified two paralogs encoding phytochrome A (phyA), GmphyA1 and GmphyA2, in soybean, a paleopolyploid species. GmphyA2 is encoded by the E4 locus responsible for photoperiod sensitivity. In photoperiod insensitive lines, GmphyA2 is inactivated by the insertion of a retrotransposon in exon 1. Here, we describe the detailed characterization of the element and its evolutionary significance inferred from the distribution of the allele that harbors the element. Structural characteristics indicated that the element, designated SORE-1, is a novel Ty1/copia-like retrotransposon in soybean, which was phylogenetically related to the Sto-4, BARE-1, and RIRE1 elements. The element was transcriptionally active, and the transcription was partially repressed by an epigenetic mechanism. Sequences homologous with SORE-1 were detected in a genome sequence database of soybean, most of which appeared silent. GmphyA2 that harbors the SORE-1 insertion was detected only in cultivated soybean lines grown in northern regions of Japan, consistent with the notion that photoperiod insensitivity caused by the dysfunction of GmphyA2 is one of genetic changes that allowed soybean cultivation at high latitudes. Taking into account that genetic redundancy is conferred by the two phyA genes, we propose a novel model for the consequences of gene duplication and transposition of retrotransposons: when the gene is duplicated, retrotransposon insertion that causes the loss of a gene function can lead to adaptive evolution while the organism is sustained by the buffering effect brought about by gene duplication.", 
"Background: Genomic imprinting is an epigenetic source of variation in quantitative traits that results from monoallelic gene expression, where commonly either only the paternally- or the maternally-derived allele is expressed. Imprinting has been shown to affect a diversity of complex traits in a variety of species. For several such quantitative traits sex-dependent genetic effects have been discovered, but whether imprinting effects also show such sex-dependence has yet to be explored. Moreover, theoretical work on the evolution of sex-dependent genomic imprinting effects makes specific predictions about the phenotypic patterns of such effects, which, however, have not been assessed empirically to date. Results: Using a genome-scan for loci affecting a set of complex growth and body composition traits from an intercross between two divergent mouse strains, we investigated possible sex-dependent imprinting effects. Our results demonstrate for the first time the existence of genomic imprinting effects that depend on sex and are not related to sex-chromosome effects. We detected a total of 13 loci on 11 chromosomes that showed significant differences between the sexes in imprinting effects. Most loci showed imprinting effects in only one sex, with eight imprinted effects found in males and six in females. One locus showed sex-dependent imprinting effects in both sexes for different traits. The absence of an imprinting effect in one sex was not necessarily indicative of the overall inactivity of the locus in that sex, as for several loci a significant additive or dominance effect was detected. Moreover, three loci exhibited significant additive effects in both sexes but their imprinting effect was restricted to one sex. Conclusion: Our results clearly show that imprinting effects can be sex-dependent and also suggest that new candidate imprinted loci can be detected when taking account of sex-specific imprinting effects. However, predictions made about the evolution of sex-dependent imprinting effects and associated phenotypic patterns cannot be unequivocally supported at present and further research into the selection pressures applied to the strains of mice used in our study is required.", 
"Modular variation of multivariate traits results from modular distribution of effects of genetic and epigenetic interactions among those traits. However, statistical methods rarely detect truly modular patterns, possibly because the processes that generate intramodular associations may overlap spatially. Methodologically, this overlap may cause multiple patterns of modularity to be equally consistent with observed covariances. To deal with this indeterminacy, the present study outlines a framework for testing a priori hypotheses of modularity in which putative modules are mathematically represented as multidimensional subspaces embedded in the data. Model expectations are computed by subdividing the data into arrays of variables, and intermodular interactions are represented by overlapping arrays. Covariance structures are thus modeled as the outcome of complex and nonorthogonal intermodular interactions. This approach is demonstrated by analyzing mandibular modularity in nine rodent species. A total of 620 models are fit to each species, and the most strongly supported are heuristically modified to improve their fit. Five modules common to all species are identified, which approximately map to the developmental modules of the mandible. Within species, these modules are embedded within larger super-modules, suggesting that these conserved modules act as building blocks from which covariation patterns are built.", 
"Sexual reproduction implies high costs, but it is difficult to give evidence for evolutionary advantages that would explain the predominance of meiotic sex in eukaryotes. A combinational theory discussing evolution, maintenance and loss of sex may resolve the problem. The main function of sex is the restoration of DNA and consequently a higher quality of offspring. Recombination at meiosis evolved, perhaps, as a repair mechanism of DNA strand damages. This mechanism is most efficient for DNA restoration in multicellular eukaryotes, because the initial cell starts with a re-optimized genome, which is passed to all the daughter cells. Meiosis acts also as creator of variation in haploid stages, in which selection can purge most efficiently deleterious mutations. A prolonged diploid phase buffers the effects of deleterious recessive alleles as well as epigenetic defects and is thus optimal for prolonged growth periods. For complex multicellular organisms, the main advantage of sexuality is thus the alternation of diploid and haploid stages, combining advantages of both. A loss of sex is constrained by several, partly group-specific, developmental features. Hybridization may trigger shifts from sexual to asexual reproduction, but crossing barriers of the parental sexual species limit this process. For the concerted break-up of meiosis-outcrossing cycles plus silencing of secondary features, various group-specific changes in the regulatory system may be required. An establishment of asexuals requires special functional modifications and environmental opportunities. Costs for maintenance of meiotic sex are consequently lower than a shift to asexual reproduction. Heredity (2009) 103, 445-457; doi:10.1038/hdy.2009.85; published online 22 July 2009", 
"Environmental factors can induce significant epigenetic changes that may also be inherited by future generations. The maternally inherited symbiont of arthropods Wolbachia pipientis is an excellent candidate as an 'environmental' factor promoting trans-generational epigenetic changes: by establishing intimate relationships with germ-line cells, epigenetic effects of Wolbachia symbiosis would be manifested as a,maternal effect', in which infection of the mother modulates the offspring phenotype. In the leafhopper Zyginidia pullula, Wolbachia feminizes genetic males, leaving them as intersexes. With the exception of male chitinous structures that are present in the last abdominal segment, feminized males display phenotypic features that are typical of females. These include ovaries that range from a typical histological architecture to an altered structure. Methylation-sensitive random amplification of polymorphic DNA profiles show that they possess a female genomic imprint. On the other hand, some rare feminized males bear testes instead of ovaries. These specimens possess a Wolbachia density approximately four orders of magnitude lower than feminized males with ovaries and maintain a male genome-methylation pattern. Our results indicate that Wolbachia infection disrupts male imprinting, which dramatically influences the expression of genes involved in sex differentiation and development, and the alteration occurs only if Wolbachia exceeds a density threshold. Thus, a new Wolbachia's role as an environmental evolutionary force, inducing epigenetic trans-generational changes, should now be considered.", 
"When in evolutionary history did long-range projectile weapons become an important component of hunting toolkits? The archeological evidence for the development of projectile weaponry is complex and generally indirect, and has led to different conclusions about the origin and spread of this technology. Lithic evidence from the Middle Stone Age (MSA) has led some researchers to suggest that true long-range projectile weaponry developed in Africa perhaps as early as 80,000 years ago, and was part of the subsistence toolkit carried by modern humans who expanded out of Africa after 50,000 years ago. Alternatively, temporal patterns in the morphology of pointed lithics has led others to posit an independent, convergent origin of projectile weaponry in Africa, the Near East, and Europe during the interval between 50,000-40,000 years ago. By either scenario, projectile weapons would not have been a component of the hunting arsenal of Neandertals, but may have been in use by European early modern humans and thus, projectile technology may have entered into the competitive dynamics that existed between these two groups. The origins of projectile weapons can be addressed, in part, through analyses of the skeletal remains of the prehistoric humans who made and used them. Habitual behavior patterns-including those related to the production and use of technology-can be imprinted on the skeleton through both genetic and epigenetic pathways. Recent studies in the field of sports medicine indicate that individuals who engage in habitual throwing have increased humeral retroversion angles in their throwing arms and a greater degree of bilateral asymmetry in retroversion angles than do non-throwers. This contribution investigates humeral torsion through analysis of the retroversion angle in samples of Eurasian Neandertals, European early modern humans of the middle and late Upper Paleolithic, and comparative samples of recent humans. This analysis was conducted under the assumption that if throwing-based projectile weaponry was used by early modern Europeans but not Neandertals, Upper Paleolithic samples should be similar to recent human groups engaged in habitual throwing in the degree of humeral retroversion in the dominant limb and in bilateral asymmetry in this feature. Neandertals on the other hand, would not be expected to show marked asymmetry in humeral retroversion. Consistent with other studies, Neandertals exhibit increased retroversion angles (decreased humeral torsion or a more posteriorly oriented humeral head) relative to most modern human samples, although this appears more likely related to body form and overall activity levels than to habitual throwing. Although Neandertals with bilaterally preserved humeri sufficient for measurement are rare (consisting of only two males and one female), levels of bilateral asymmetry in humeral retroversion are low, suggesting a lack of regular throwing. While patterning across fossil and comparative samples in levels of humeral retroversion was not clear cut, males of both the middle and late Upper Paleolithic demonstrate a high level of bilateral asymmetry, comparable to or in excess of that seen in samples of throwing athletes. This may indicate habitual use of throwing-based projectile weaponry by middle Upper Paleolithic times. Small sample sizes and relatively great variance in the fossil samples makes these results, however, suggestive rather than conclusive. (C) 2008 Elsevier Ltd. All rights reserved.", 
"Satellite DNA is a major component of centromeric heterochromatin in most multicellular eukaryotes, where it is typically organized into megabase-sized tandem arrays. It has recently been demonstrated that small interfering RNAs (siRNAs) processed from centromeric satellite repeats can be involved in epigenetic chromatin modifications which appear to underpin centromere function. However, the structural organization and evolution of the centromeric satellite DNA is still poorly understood. We analyzed the centromeric satellite repeat arrays from rice chromosomes 1 and 8 and identified higher order structures and local homogenization of the CentO repeats in these 2 centromeres. We also cloned the CentO repeats from the CENH3-associated nucleosomes by a chromatin immunoprecipitation (ChIP)-based method. Sequence variability analysis of the ChIPed CentO repeats revealed a single variable domain within the repeat. We detected transcripts derived from both strands of the CentO repeats. The CentO transcripts are processed into siRNA, suggesting a potential role of this satellite repeat family in epigenetic chromatin modification.", 
"DNA methylation is one of the epigenetic and hereditary mechanisms regulating genetic expression in mammalian cells. In this review, we propose how certain natural agents, through their dietary consumption, could induce changes in physiological aspects in mammalian mothers, leading to alterations in DNA methylation patterns of the developing fetus and to the emergence of new phenotypes and evolutionary change. Nevertheless, we hypothesize that this process would require (i) certain key periods in the ontogeny of the organism where the environmental stimuli could produce effects, (ii) particular environmental agents as such stimuli, and (iii) that a genomic persistent change be consequently produced in a population. Depending on the persistence of the environmental stimuli and on whether the affected genes are imprinted genes, induced changes in DNA methylation patterns could become persistent. Moreover, some fragments could be more frequently methylated than others over several generations, leading to biased base change and evolutionary consequences.", 
"Changes in DNA methylation patterns during embryo development and differentiation processes are linked to the transcriptional plasticity of our genome. However, little is known about the evolutionary conservation of DNA methylation patterns and the evolutionary impact of epigenetic differences between closely related species. Here we compared the methylation patterns of CpG islands (CGIs) in the promoter regions of seven genes in humans and chimpanzees. We identified a block of CpGs in the cell cycle-related kinase (CCRK) gene that is more methylated in the adult human cortex than in the chimpanzee cortex and, in addition, it exhibits considerable intraspecific variation both in humans and chimpanzees. The species-specifically methylated region (SMR) lies between the almost completely methylated 5' region and the completely demethylated 3' region of the presumed CCRK CGI promoter. It is part of an Alu-Sg1 repeat that has been integrated into the promoter region in a common ancestor of humans and New World monkeys. This SMR is relatively hypomethylated in the rhesus monkey cortex and more or less completely methylated in the baboon cortex, indicating extraordinary methylation dynamics during primate evolution. The mRNA expression level of CCRK has also changed during the course of primate evolution. CCRK is expressed at much higher levels in human and baboon cortices, which display an average SMR methylation of 70% and 100%, respectively, than in chimpanzee and rhesus macaque cortices with an average SMR methylation of 35% and 40%, respectively. The observed evolutionary dynamics suggests a possibility that CCRK has been important for evolution of the primate brain.", 
"The goal of this short review is to consider the interrelated phenomena of phenotypic variation and genetic constraint with respect to plant diversity. The unique aspects of plants, including sessile habit, modular growth and diverse developmental programs expressed at the phytomer level, merit a specific examination of the genetic basis of their phenotypic variation, and how they experience and escape genetic constraint. Numerous QTL studies with wild and domesticated plants reveal that most phenotypic traits are polygenic but vary in the number and effect of the loci contributing, from a few loci of large effects to many with small effects. Further, somatic mutations, developmental plasticity and epigenetic variation, especially gene methylation, can contribute to increases in phenotypic variation. The flip side of these processes, genetic constraint, can similarly be the result of many factors, including pleiotropy, canalization and genetic redundancy. Genetic constraint is not only a mechanism to prevent change, however, it can also serve to direct evolution along certain paths. Ultimately, genetic constraint often comes full circle and is released through events such as hybridization, genome duplication and epigenetic remodeling. We are just beginning to understand how these processes can operate simultaneously during the evolution of ecologically important traits in plants.", 
"Developmentally regulated genome rearrangements (DRGR)-processes that alter genomes either in specific cells or during specific life cycle stages-are widespread throughout eukaryotes. This contrasts with the view that genome structure and content remain essentially constant throughout an organism's life cycle. Here we review three categories of developmentally regulated genome processing in eukaryotes: genome-wide rearrangements, targeted rearrangements, and a special case of amplification of ribosomal DNA genes. Mapping these types of DRGR onto eukaryotic phylogeny indicates that each type of processing is found in multiple independent lineages. We propose that such genome rearrangements were present within the last common ancestor of extant eukaryotes, and that future research will yield evidence of homologous epigenetic mechanisms underlying genome processing among diverse eukaryotes.", 
"Rapid recent developments in DNA sequencing and genetic marker technologies call for the establishment of cost-effective, automated phenotyping assays for evolutionary biology and systematics, so that the effects of DNA polymorphisms and epigenetic changes on the phenotype call be evaluated. We discuss the use of digital image-based morphometrics in evolutionary biology and systematics with special emphasis oil Studies of taxa with porous genomes, i.e., taxa that do not conform to the traditional view of whole-genome isolation between species. We outline the phenomenon of the 'phenotypic mosaic' in taxa with porous genomes using well-documented examples from the literature and describe three important challenges arising for taxonomists: (1) character conflict in phylogenetic studies, (2) biased sampling of traits in morphological Studies, and (3) cryptic ecological speciation. We demonstrate the use of geometric morphometrics using a combined molecular and morphometric dataset from an interspecific hybrid zone between two divergent Eurasian species of Populus, P. alba (white poplar) and P. tremula (European aspen). Elliptic Fourier analysis (EFA)-based morphometric data were collected for 527 leaf specimens from 84 trees with known genomic composition as determined by a set of 30 nuclear DNA microsatellites. In addition, to demonstrate the case of scoring functionally relevant phenotypes via digital image analysis, quantitative differences in leaf reflectance were examined and their structural basis determined using scanning electron microscopy (SEM). The EFA results indicate a heritable inter-individual component for symmetric aspects and all important intra-individual component for asymmetric aspects of variation in leaf outlines. Symmetric traits displayed a striking variety of phenotypes in hybrids compared to their parental species, consistent with the notion of the phenotypic mosaic. Linear discriminant analysis of these morphometric traits revealed (1) clear differentiation between parental species and (2) divergence between recombinant hybrids and their sympatric backcross parent P. alba, mediated primarily by two P. tremula-like and two transgressive traits. Our results demonstrate the usefulness of geometric morphometrics to interrogate multiple independent phenotypic characters and detect individual traits affected by introgression and divergence in taxa with porous genomes. Digital image-based morphometrics holds great promise for large-scale Studies of relationships between DNA polymorphism and phenotypes in evolutionary biology.", 
"The interaction between maternally provided environment and offspring genotype is a major determinant of offspring development and fitness in many organisms. Recent research has demonstrated that not only genetic effects, but also epigenetic effects may be subject to modifications by the maternal environment. Genomic imprinting resulting in parent-of-origin-dependent gene expression is among the best studied of epigenetic effects. However, very little is known about the degree to which genomic imprinting effects can be modulated by the maternally provided environment, which has important implications for phenotypic plasticity. In this study, we investigated this unresolved question using a cross-fostering design in which mouse pups were nursed by either their own or an unrelated mother. We scanned the entire genome to search for quantitative trait loci whose effects depend on cross-fostering and detected 10 of such loci. Of the 10 loci, 4 showed imprinting by cross-foster interactions. Inmost cases, the interaction effect was due to the presence of an effect in either cross-fostered or non-cross-fostered animals. Our results demonstrate that genomic imprinting effects may often be modified by the maternal environment and that such interactions can impact key fitness-related traits suggesting a greater plasticity of genomic imprinting than previously assumed.", 
"In the early 1930s, the synthesis of Darwinian natural selection, mutation, and Mendelian genetics gave rise to the paradigm of 'modern Darwinism', also known as 'neo-Darwinism'. This has contributed greatly to our understanding. But increasing knowledge of other mechanisms, including endosymbiosis, genetic and genomic duplication, polyploidy, hybridization, epigenetics, horizontal gene transfer in prokaryotes, and the modern synthesis of embryonic development and evolution, has widened our horizons to a diversity of possibilities for change. All of these can be gathered under the umbrella concept of 'genomic creativity', which, in partnership with natural selection, affords a more comprehensive modern explanation of evolution. (c) 2006 The Linnean Society of London, Biological Journal of the Linnean Society, 2006, 88, 655-672.", 
"The primary goal of virtually all organisms is to produce genetic offspring, thereby passing on their genes to future generations. Offspring production, however, is limited by available resources within an environment. Moreover, distributing sufficient energy among competing physiological systems is challenging and can result in trade-offs between self-maintenance and offspring investment when resources are limited. In the current study, we tested the hypothesis that the adipose hormone leptin is involved in mediating energetic trade-offs between competing physiological systems. Specifically, we tested the effects of elevated maternal leptin on investment into offspring production versus self maintenance (immune function), in the Siberian hamster (Phodopus sungorus). The current study provides the first evidence that leptin serves as a signal to mothers of available energy resulting in epigenetic effects. Therefore, elevated leptin allows females to retain more embryos to parturition, and rear more offspring to weaning via reduced maternal infanticide. Innate immune response was suppressed seemingly as a result of these enlarged litters, suggesting that the observed fitness increase is not without costs to the mother. Collectively, these findings suggest that leptin plays a critical role in allowing mothers to determine how much energy to invest in the production and care of young versus self-maintenance.", 
"Sequential segmentation from a posterior proliferative zone is considered to be the primitive mechanism of segmentation in arthropods. Several studies of embryonic and post-embryonic development and gene expression suggest that this occurs in all major arthropod taxa. Sequential segmentation is often associated with the idea of posterior production of body units that accumulate along the main body axis. However, the precise mechanism of sequential segmentation has not been identified yet, and, while searching for the genetic circuitry able to generate a first periodic pattern in the embryo, we can at least outline the distinctive role in segmentation of a proliferative zone. A perusal of myriapod segmentation patterns suggests that these patterns result from multi-layered developmental processes, where gene expression and epigenetic mechanisms interact in a nonstrictly hierarchical way. The posterior zone is possibly a zone of periodic signal production, but, in general, the resulting segmental pattern is not completely attributable to the activity of the signal generator. In this sense, a posterior proliferative zone would be more a segmental organizer than a segment generator.", 
"The controversy surrounding the alleged Lamarckian fraud of Paul Kammerer's midwife toad experiments has intrigued generations of biologists. A re-examination of his descriptions of hybrid crosses of treated and nontreated toads reveals parent-of-origin effects like those documented in epigenetic inheritance. Modification of the extracellular matrix of the egg as described by Kammerer provides a plausible cause for altered gene methylation patterns. Traits such as altered egg and adult body size in Kammerer's treated toads are inherited epigenetically in other tetrapods. A preliminary model involving the environmental silencing of a maternally inherited allele can be attempted to explain the midwife toad experiments. Given available molecular tools and our current understanding of epigenetics, new experimentation with the midwife toad is strongly encouraged. J. Exp. Zool. (Mol. Dev. Evol.) 312B:667-678, 2009. (C) 2009 Wiley-Liss, Inc.", 
"So far, in maize, three classes of mutants involved in phytic acid biosynthesis have been isolated: lpa1, lpa2 and lpa3. In 2007, a gene tagging experiment performed by Shi et al. found that mutations in ZmMRP4 ( multidrug resistance-associated proteins 4) gene cause lpa1 phenotype. In previous studies, we isolated and described a single recessive lpa mutation ( originally named lpa241), which was allelic to the lpa1-1 mutant, and was consequently renamed lpa1-241. It showed a decrease in the expression of the myo-inositol (Ins)-3-phosphate synthase gene (mips1S). In this study, we present genetic and molecular analyses of the lpa1-241 mutation that indicate an epigenetic origin of this trait, that is, a paramutagenic interaction that results in meiotically heritable changes in ZmMRP4 gene expression, causing a strong pleiotropic effect on the whole plant. The use of a 5-Azacytidine treatment provided data suggesting an association between gene methylation and the lpa1-241 phenotype. To our knowledge, this is the first report of a paramutagenic activity not involving flavonoid biosynthesis in maize, but regarding a key enzyme of an important metabolic pathway in plants.", 
"Sex is generally thought of as meiosis, conjugation, and syngamy, with the primary function of sex believed to be genetic mixing. However, conjugation does not occur with complete automixis, whereas syngamy does not occur with restitutional automixis. Self sex in the forms of automixis and autogamy does not include genetic mixing. Yet sex, including self sex, is necessary for most eukaryotic lineages. What is the purpose of sex without genetic mixing? Obligate self sex is not an evolutionary dead end, but holds the key to understanding the evolutionary origin, function, maintenance, and ubiquity of sex. We extend the rejuvenescence hypothesis that sex provides a necessary developmental reset for multicellular eukaryotes and even many unicellular eukaryotes. Sex reduces additive genetic variance of epigenetic signals, especially cytosine methylation, and of ploidy levels. Furthermore, we argue that syngamy is a modified form of meiosis that maintains ploidy and resets epigenetic signals. Epigenetic resetting is consistent with sex being induced by starvation or desiccation. Diminution of additive genetic variance is consistent with the origin and maintenance of an adaptive trait, sex, that has been present for approximately two billion years. (C) 2009 The Linnean Society of London, Biological Journal of the Linnean Society, 2009, 98, 707-728.", 
"5S ribosomal DNA is a highly conserved tandemly repeated multigenic family. As suggested for a long time, we have shown that only a fraction of the 5S rRNA genes are expressed in Arabidopsis thaliana. In Xenopus laevis, there is a developmental control of the expression of the 5S rRNA genes with only one of the two 5S rDNA families expressed during oogenesis. For both Arabidopsis and Xenopus, the strongest transcription of 5S rRNA, respectively in the seed and during oogenesis is correlated with heterogeneity in the transcribed 5S rRNAs. Epigenetic mechanisms such as modification of the chromatin structure are involved in the transcriptional regulation of the 5S rRNA genes in both organisms. In Arabidopsis, two silencing pathways, methylation-dependent (RNAi) and methylationin-dependent (MOM pathway), are involved in the silencing of a 5S rDNA fraction.", 
"The purpose of this study is to test two competing models regarding the origins of Early Intermediate Period (AD 200-750) sacrificial victims from the Huacas de Moche site using the matrix correlation method. The first model posits the sacrificial victims represent local elites who lost competitions in ritual battles with one another while the other model suggests the victims were nonlocal warriors captured during warfare with nearby polities. We estimate biodistances for sacrificial victims from Huaca de la Luna Plaza 3C (AD 300550) with eight previously reported samples from the north coast of Peru using both the mean measure of divergence (MMD) and Mahalanobis' distance (d(2)). Hypothetical matrices are developed based upon the assumptions of each of the two competing models regarding the origins of Moche sacrificial victims. When the MMD matrix is compared to the two hypothetical matrices using a partial-Mantel test (Smouse et al.: Syst Zool 35 (1986) 627-632), the ritual combat model (i.e. local origins) has a low and nonsignificant correlation (r = 0.134, P = 0.163), while the nonlocal origins model is highly correlated and significant (r = 0.688, P = 0.001). Comparisons of the d(2) results and the two hypothetical matrices also produced low and nonsignificant correlation for the ritual combat model (r = 0.210, P = 0.212), while producing a higher and statistically significant result with the nonlocal origins model (r = 0.676, P = 0.002). We suggest that the Moche sacrificial victims represent nonlocal warriors captured in territorial combat with nearby competing polities.", 
"Studies on the origin of species have focused largely on anatomy, yet animal populations are generally limited by energy. Animals can adapt to available energy resources at three levels: (1) evolution of different anatomical forms between groups of animals through nuclear DNA (nDNA) mutations, permitting exploitation of alternative energy reservoirs and resulting in new species with novel niches, (2) evolution of different physiologies within intraspecific populations through mutations in mitochondrial DNA (mtDNA) and nDNA bioenergetic genes, permitting adjustment to energetic variation within a species' niche, and (3) epigenomic regulation of dispersed bioenergetic genes within an individual via mitochondrially generated high-energy intermediates, permitting individual adjustment to environmental fluctuations. Because medicine focuses on changes within our species, clinically relevant variation is more likely to involve changes in bioenergetics than anatomy. This may explain why mitochondrial diseases and epigenomic diseases frequently have similar phenotypes and why epigenomic diseases are being found to involve mitochondrial dysfunction. Therefore, common complex diseases may be the result of changes in any of a large number of mtDNA and nDNA bioenergetic genes or to altered epigenomic regulation of these bioenergetic genes. All of these changes result in similar bioenergetic failure and consequently related phenotypes.", 
"We discuss the changing use of epigenetics, a term coined by Conrad Waddington in the 1940s, and how the epigenetic approach to development differs from the genetic approach. Originally, epigenetics referred to the study of the way genes and their products bring the phenotype into being. Today, it is primarily concerned with the mechanisms through which cells become committed to a particular form or function and through which that functional or structural state is then transmitted in cell lineages. We argue that modern epigenetics is important not only because it has practical significance for medicine, agriculture, and species conservation, but also because it has implications for the way in which we should view heredity and evolution. In particular, recognizing that there are epigenetic inheritance systems through which non-DNA variations can be transmitted in cell and organismal lineages broadens the concept of heredity and challenges the widely accepted gene-centered neo-Darwinian version of Darwinism.", 
"Allopolyploid speciation is widespread in plants, yet the molecular requirements for successful orchestration of coordinated gene expression for two divergent and reunited genomes are poorly understood. Recent studies in several plant systems have revealed that allopolyploid genesis under both synthetic and natural conditions often is accompanied by rapid and sometimes evolutionarily conserved epigenetic changes, including alteration in cytosine methylation patterns, rapid silencing in ribosomal RNA and protein-coding genes, and de-repression of dormant transposable elements. These changes are inter-related and likely arise from chromatin remodeling and its effects on epigenetic codes during and subsequent to allopolyploid formation. Epigenetic modifications could produce adaptive epimutations and novel phenotypes, some of which may be evolutionarily stable for millions of years, thereby representing a vast reservoir of latent variation that may be episodically released and made visible to selection. This epigenetic variation may contribute to several important attributes of allopolyploidy, including functional diversification or subfunctionalization of duplicated genes, genetic and cytological diploidization, and quenching of incompatible inter-genomic interactions that are characteristic of allopolyploids. It is likely that the evolutionary success of allopolyploidy is in part attributable to epigenetic phenomena that we are only just beginning to understand. (C) 2003 Elsevier Inc. All rights reserved.", 
"Novel phenotypes often arise in generations immediately following polyploidization. Previous studies have shown that separate lineages derived from a resynthesized Brassica napus allopolyploid rapidly evolved heritable differences in flowering time. These early-flowering and late-flowering polyploid lines were expected to be genetically identical because they were derived from a single, chromosome-doubled amphihaploid plant. In this study, we investigated the molecular genetic basis for these flowering time differences. We assessed the diploid B. rapa and B. oleracea parents and the early- and late-flowering B. napus lineages for changes in genome structure, and for changes in transcript levels of four sets of FLOWERING LOCUS C (FLC) genes. No such changes were observed for BnFLC1, but we detected chromosomal rearrangements (e.g. de novo non-reciprocal transpositions) and changes in transcript level for BnFLC2 and BnFLC3 between the early- and late-flowering B. nap us. A chromosomal rearrangement of a genomic segment containing BnFLC3 was responsible for 29% of the phenotypic variation among the B. napus lines. Expression of BnFLC5 was silenced in all polyploids, although no changes in genome structure were detected. An ongoing investigation of 50 identical B. napus allopolyploids may further reveal the dynamics of changes in phenotype, genome and transcriptome at the early stages in polyploid evolution. (C) 2004 The Linnean Society of London.", 
"Reconstructing the transition to bipedality is key to understanding early hominin evolution. Because it is the best-known early hominin species, Australopithecus afarensis forms a baseline for interpreting locomotion in all early hominins. While most researchers agree that A. afarensis individuals were habitual bipeds, they disagree over the importance of arboreality for them. There are two main reasons for the disagreement. First, there are divergent perspectives on how to interpret primitive characters. Primitive traits may be retained by stabilizing selection, pleiotropy, or other ontogenetic mechanisms. Alternately, they could be in the process of being reduced, or they simply could be selectively neutral. Second, researchers are asking fundamentally different questions about the fossils. Some are interested in reconstructing the history of selection that shaped A. afarensis, while others are interested in reconstructing A. afarensis behavior. By explicitly outlining whether we are interested in reconstructing selective history or behavior, we can develop testable hypotheses to govern our investigations of the fossils. To infer the selective history that shaped a taxon, we must first consider character polarity. Derived traits that enhance a particular function, are found to be associated with that function in extant homologs, and that epigenetically sensitive data indicate were actually being used for that function, can be interpreted as adaptations. The null hypothesis to explain the retention of primitive traits is that of selective neutrality, or nonaptation. Disproving this requires demonstration of active stabilizing or negative selection (disaptation). Stabilizing selection can be inferred when primitive traits compromise a derived function clearly of adaptive value. Prolonged stasis, continued use of the trait for a particular function, or no change in variability in the trait are evidence that can support a hypothesis of adaptation for primitive traits, but still do not falsify the null hypothesis. Disaptation, or negative selection, should result in a trait being reduced or lost. To infer the behaviors of a fossil species, we must first determine its adaptations, use this to make hypotheses about its behavior, and test these hypotheses using epigenetically sensitive traits that are modified by an individual's activity pattern. When the A. afarensis data are evaluated using this framework, it is clear that these hominins had undergone selection for habitual bipedality, but the null hypothesis of nonaptation to explain the retention of primitive, ape-like characters cannot be falsified at present. The apparent stasis in Australopithecus postcranial form is currently the strongest evidence for stabilizing selection maintaining its primitive features. Evidence from features affected by individual behaviors during ontogeny shows that A. afarensis individuals were habitually traveling bipedally, but evidence presented for arboreal behavior so far is not conclusive. By clearly identifying the questions we are asking about early hominin fossils, refining our knowledge about character polarities, and elucidating the factors influencing morphology, we will be able to progress in our understanding of the posture and locomotion of A. afarensis and all early hominins. Am J Phys Anthropol 45:185-215, 2002. (C) 2002 Wiley-Liss, Inc.", 
"The idea of genetic assimilation, that environmentally induced phenotypes may become genetically fixed and no longer require the original environmental stimulus, has had varied success through time in evolutionary biology research. Proposed by Waddington in the 1940s, it became an area of active empirical research mostly thanks to the efforts of its inventor and his collaborators. It was then attacked as of minor importance during the hardening of the neo-Darwinian synthesis and was relegated to a secondary role for decades. Recently, several papers have appeared, mostly independently of each other, to explore the likelihood of genetic assimilation as a biological phenomenon and its potential importance to our understanding of evolution. In this article we briefly trace the history of the concept and then discuss theoretical models that have newly employed genetic assimilation in a variety of contexts. We propose a typical scenario of evolution of genetic assimilation via an intermediate stage of phenotypic plasticity and present potential examples of the same. We also discuss a conceptual map of current and future lines of research aimed at exploring the actual relevance of genetic assimilation for evolutionary biology.", 
"In the past few years we have analysed alterations in genome structure and expression that occur in wheat upon allopolyploidization. Our major findings in natural and synthetic allopolyploid wheat are reviewed here. It was found that allopolyploidization brings about rapid genome evolution through the instantaneous generation of a variety of cardinal genetic and epigenetic alterations comprising: (1) non-random elimination of coding and non-coding DNA sequences, (2) epigenetic changes such as DNA methylation of coding and non-coding DNA leading, among others, to gene silencing, and (3) activation of retroelements, which in turn alters the expression of adjacent genes. These changes were reproducible, occurring in the F1 hybrids or in the first generation(s) of a series of nascent allopolyploids corresponding to various interspecific and intergeneric combinations. Moreover, these changes were similar to those that occurred twice in nature: first, at the transition from diploid to tetraploid wheat (similar to0.5 Mya) and, second, at the transition from tetraploid to hexaploid wheat (similar to9500 years ago). Elimination of non-coding sequences augments the differentiation of homoeologous chromosomes at the polyploid level, thus increasing the physical divergence between homoeologues and contributing to the diploid-like meiotic behaviour of polyploid wheat. Transcriptional and post-transcriptional alterations of gene activity, including transcriptional activation of retroelements, led to novel expression patterns. These phenomena emphasize the plasticity of the genome with regard to both structure and gene expression. This plasticity in turn might improve the adaptability of the newly formed allopolyploids and facilitate their rapid and successful establishment in nature. (C) 2004 The Linnean Society of London.", 
"One continuous thread in this volume is the name of Conrad H. Waddington (1905-1975), the developmental biologist known as the inventor of the term epigenetics. After some biographical notes on his life, this article explores the meaning of the Waddingtonian equation and the context wherein it was developed. This equation holds that epigenesis + genetics = epigenetics, and refers in retrospect to the debate on epigenesis versus preformationism in neoclassical embryology. Whereas Waddington actualized this debate by linking epigenesis to developmental biology and preformation to genetics, thereby stressing the importance of genetic action in causal embryology, today's epigenetics more and more offers the possibility to enfeeble biological thinking in terms of genes only, as it expands the gene-centric view in biology by introducing a flexible and pragmatically oriented hierarchy of crucial genomic contexts that go beyond the organism.", 
"In plants, naturally occurring methylation of genes can affect the level of gene expression. Variation among individuals in the degree of methylation of a gene, termed epialleles, produces novel phenotypes that are heritable across generations. To date, ecologically important genes with methylated epialleles have been found to affect floral shape, vegetative and seed pigmentation, pathogen resistance and development in plants. Currently, the extent to which epiallelic variation is an important common contributor to phenotypic variation in natural plant populations and its fitness consequences are not known. Because epiallele phenotypes can have identical underlying DNA sequences, response to selection on these phenotypes is likely to differ from expectations based on traditional models of microevolution. Research is needed to understand the role of epialleles in natural plant populations. Recent advances in molecular genetic techniques could enable population biologists to screen for epiallelic variants within plant populations and disentangle epigenetic from more standard genetic sources of phenotypic variance, such as additive genetic variance, dominance variance, epistasis and maternal genetic effects.", 
"Spartina anglica arose during the end of the 19th century in England by hybridization between the indigenous Spartina maritima and the introduced East American Spartina alterniflora and following genome duplication of the hybrid (S. x townsendii). This system allows investigations of the early evolutionary changes that accompany stabilization of a new allopolyploid species in natural populations. Various molecular data indicate that S. anglica has resulted from a unique parental genotype. This young species contains two distinctly divergent homoeologous genomes that have not undergone extensive change since their reunion. No burst of retroelements has been encountered in the F-1 hybrid or in the allopolyploid, suggesting a 'structural genomic stasis' rather than 'rapid genomic changes'. However, modifications of the methylation patterns in the genomes of S. x townsendii and S. anglica indicate that in this system, epigenetic changes have followed both hybridization and polyploidization. (C) 2004 The Linnean Society of London.", 
"We investigated the. randomness and uniqueness of human iris patterns by mathematically comparing 2.3 million different pairs of eve images. The phase structure of each iris pattern was extracted by demodulation with quadrature wavelets spanning several scales of analysis. The resulting distribution of phase sequence variation anion different eyes was precisely binomial, revealing 244 independent degrees of freedom. This amount of statistical variability corresponds to an entropy (information density) of about 3.2 bits mm(-2) over the iris. It implies that the probability of two different irides agreeing by chance in more than 70% of their phase sequence is about one in 7 billion. We also compared images of genetically identical irides, from the left and right eyes of 324 persons, and from monozygotic twins. Their relative phase sequence variation generated the same statistical distribution as did unrelated eyes. This indicates that apart from overall form and colour. iris patterns are determined epigenetically by random events in the morphogenesis of this tissue. The resulting diversity, and the combinatorial complexity created by so many dimensions of random variation, mean that the failure of a simple test of statistical independence performed on iris patterns can serve as a reliable rapid basis for automatic personal identification.", 
"The study of evolution has increasingly incorporated considerations of history, scale, and hierarchy, in terms of both the origin of variation and the sorting of that variation. Although the macroevolutionary exploration of developmental genetics has lust begun, considerable progress has been made in understanding the origin of evolutionary novelty in terms of the potential for coordinated morphological change and the potential for imposing uneven probabilities on different evolutionary directions. Global or whole-organism heterochrony, local heterochrony (affecting single structures, regions, or organ systems) and heterotopies (changes in the location of developmental events), and epigenetic mechanisms (which help to integrate the developing parts of an organism into a functional whole) together contribute to profound nonlinearities between genetic and morphologic change, by permitting the generation and accommodation of evolutionary novelties without pervasive, coordinated genetic changes; the limits of these developmental processes are poorly understood, however. The discordance across hierarchical levels in the production of evolutionary novelties through time, and among latitudes and environments, is an intriguing paleontological pattern whose explanation is controversial, in part because separating effects of genetics and ecology has proven difficult. At finer scales, species in the fossil record tend to be static over geologic time, although this stasis-to which there are gradualistic exceptions-generally appears to be underlain by extensive, nondirectional change rather than absolute invariance. Only a few studies have met the necessary protocols for the analysis of evolutionary tempo and mode at the species level, and so the distribution of evolutionary patterns among clades, environments, and modes of life remains poorly understood. Sorting among taxa is widely accepted in principle as an evolutionary mechanism, but detailed analyses are scarce; if geographic range or population density can be treated as traits above the organismic level, then the paleontological and macroecological literature abounds in potential raw material for such analyses. Even if taxon sorting operates on traits that are not emergent at the species level, the differential speciation and extinction rates can shape large-scale evolutionary patterns in ways that are not simple extrapolations from shortterm evolution at the organismal level. Changes in origination and extinction rates can evidently be mediated by interactions with other clades, although such interactions need to be studied in a geographically explicit fashion before the relative roles of biotic and physical factors can be assessed. Incumbency effects are important at many scales, with the most dramatic manifestation being the postextinction diversifications that follow the removal of incumbents. However, mass extinctions are evolutionarily important not only for the removal of dominant taxa, which can occur according to rules that differ from those operating during times of lower extinction intensity, but also for the dramatic diversifications that follow upon the removal or depletion of incumbents. Mass extinctions do not entirely reset the evolutionary clock, so survivors can exhibit unbroken evolutionary continuity trends that suffer setbacks but then resume, or failure to participate in the recovery.", 
"It is well established that asexually reproducing viruses and prokaryotes mutate rapidly. In contrast, the eukaryotic clone is often still treated as if it is genetically homogeneous within and between populations, i.e. that it is assumed to show genetic fidelity However, such fidelity has rarely been tested empirically using the range of high-resolution molecular markers now available, culminating with direct sequencing of the DNA. If such a biological entity as a 'clone' really did exist, it would be a fantastic entity, differing from everything else known in biology, i.e. it would possess a population mean but no variance for any particular trait. It would not be amenable to selection and adaptive variation and would thus be unchanging in time and space. In this paper, we argue that the general acceptance of clonal fidelity is a scientific convenience, since the rate of asexual reproduction of eukaryotes is not as fast as that of bacteria and hence it is easier to accept fidelity as a 'fact' rather than test for it. We propose that part of the acceptance of fidelity may have a cultural basis and thereby is a kind of 'pre-Darwinian relic'. Instead, a clonal genotype is perhaps largely a function of marker resolution, i.e. dependent on the number and type of markers employed. If this is so and were enough of the genome explored, perhaps each individual within a clone would be found to differ genetically at particular regions of the chromosomes. The question of what constitutes a clone is not just a semantic one and impacts directly on recent attempts to understand and produce 'artificial' clones, especially of mammals. New research is already confirming that mutations and epigenetic influences play a crucial role in the success of cloning attempts. (C) 2003 The Linnean Society of London.", 
"We have examined the methylation status of the zebrafish genome during early embryogenesis and we find evidence that methylation fluxes do occur in that organism. The parental genetic contributions to the zygote are, initially, differently methylated with the genome of the sperm being hypermethylated relative to the genome of the oocyte. Post-fertilization there is an immediate decrease in methylation of the embryonic genome but the methylation begins to increase rapidly and is re-established by the gastrulation stage. These results are consistent with the results of Santos et al. (Dev Biol 241:172-182, 2002), who examined the methylation of early mouse embryos, and this conservation argues that demethylation/re-methylation is an important part of vertebrate development.", 
"The crop species within the genus Brassica have highly replicated genomes. Three base 'diploid' species, Brassica oleracea, B. nigra and B. rapa, are likely ancient polyploids, and three derived allopolyploid species, B. carinata, B. juncea and B. napus, are created from the interspecific hybridization of these base genomes. The base Brassica genome is thought to have hexaploid ancestry, and both recent and ancient polyploidization events have been proposed to generate a large number of genome rearrangements and novel genetic variation for important traits. Here, we revisit and refine these hypotheses. We have examined the B. oleracea linkage map using the Arabidopsis thaliana genome sequence as a template and suggest that there is strong evidence for genome replication and rearrangement within the base Brassicas, but less evidence for genome triplication. We show that novel phenotypic variation within the base Brassicas can be achieved by replication of a single gene, BrFLC, that acts additively to influence flowering time. Within the derived allopolyploids, intergenomic heterozygosity is associated with higher seed yields. Some studies have reported that de novo genomic variation occurs within derived polyploid genomes, whereas other studies have not detected these changes. We discuss reasons for these different findings. Large translocations and tetrasomic inheritance can explain some but not all genomic changes within the polyploids. Transpositions and other small-scale sequence changes probably also have contributed to genomic novelty. Our results have shown that the Brassica genomes are remarkably plastic, and that polyploidy generates novel genetic variation through gene duplication, intergenomic heterozygosity and perhaps epigenetic change. (C) 2004 The Linnean Society of London.", 
"Gene duplication is commonly regarded as the main evolutionary path toward the gain of a new function. However, even with gene duplication, there is a loss-versus-gain dilemma: most newly born duplicates degrade to pseudogenes, since degenerative mutations are much more frequent than advantageous ones. Thus, something additional seems to be needed to shift the loss versus gain equilibrium toward functional divergence. We suggest that epigenetic silencing of duplicates might play this role in evolution. This study began when we noticed in a previous publication (Lynch M, Conery JS [2000] Science 291:1151-1155) that the frequency of functional young gene duplicates is higher in organisms that have cytosine methylation (H. sapiens, M. musculus, and A. thaliana) than in organisms that do not have methylated genomes (S. cerevisiae, D. melanogaster, and C. elegans). We find that genome data analysis confirms the likelihood of much more efficient functional divergence of gene duplicates in mammals and plants than in yeast, nematode, and fly. We have also extended the classic model of gene duplication, in which newly duplicated genes have exactly the same expression pattern, to the case when they are epigenetically silenced in a tissue- and/or developmental stage-complementary manner. This exposes each of the duplicates to negative selection, thus protecting from pseudogenization. Our analysis indicates that this kind of silencing (i) enhances evolution of duplicated genes to new functions, particularly in small populations, (ii) is quite consistent with the subfunctionalization model when degenerative but complementary mutations affect different subfunctions of the gene, and (iii) furthermore, may actually cooperate with the DDC (duplication-degeneration-complementation) process.", 
"Aphid life cycles can encompass cyclical parthenogenesis, obligate parthenogenesis, obligate parthenogenesis with male production and an intermediate 'bet-hedging' strategy where an aphid genotype will over-winter by continuing to reproduce by parthenogenesis and by investment in sexually produced eggs. In this paper, we focus on aphid lineages that reproduce entirely parthenogenetically (asexual aphids), in contrast to those that have any sexual forms in the annual cycle. Using modern molecular techniques, aphid biologists have made many empirical observations showing that asexual lineages are widespread both geographically and temporally. Indeed, we are collectively beginning to gather data on the evolution and persistence of these lineages through time. Here we review aphid karyology and parthenogenesis, both essential for interpretation of the molecular and ecological evolution of aphid asexual lineages. We describe the growing list of studies that have identified aphid genotypes that are both temporally and geographically widespread. We then collate examples of molecular and chromosomal evolution in asexual aphids and review the literature pertaining to phenotypic evolution and ecological diversification of asexual aphid lineages. In addition, we briefly discuss the potential of bacterial endosymbionts and epigenetic effects to influence the evolution of asexual aphid lineages. Lastly we provide a list of aphid taxa believed to be obligately asexual. This will be a useful resource for those seeking parthenogenetic animals as study systems. In conclusion, we present guidelines for the use of the term clone in aphid biology and stress the need for well-designed and well-executed studies examining the potential of asexual aphid lineages for adaptive evolution. (C) 2003 The Linnean Society of London.", 
"We suggest simulating evolution of complex organisms using a model constrained solely hv the requirement of robustness in its expression patterns. This scenario is illustrated by evolving discrete logical networks with epigenetic properties. Evidence for dynamical features in the evolved networks is found that carl be related to biological observables.", 
"Several models of speciation suggest that in species that are phenotypically plastic, selection can act on phenotypic variation that is environmentally induced in the earliest stages of divergence. One trait that could be subject to this process is foraging behaviour, where discrete foraging strategies are common. One species which is highly plastic in the expression of phenotype, the Arctic charr, Salvelinus alpinus (L.), is characterized by discrete variation in the anatomy of the head and mouthparts. These traits have been shown to have a functional significance, but the expression of which is thought to be at least partly phenotypically plastic. Here we test the hypothesis that foraging behaviour may regulate the anatomy of the head and mouthparts in Arctic charr. In a dyad experiment, size-matched pairs of fish from a mixed family group were fed a diet of either Mysis (a hard-bodied shrimp) or Chironomid larvae. Nine morphometric measures of head dimensions that describe wild trophic morphs were measured at the start of the experiment and 24 weeks later. Principal component scores of size-corrected morphometric measures showed highly significant differences between fish exposed to the two diets. Univariate ANOVA analysis of the head morphometric variables showed that fish fed on Chironomids developed longer, wider jaws, longer heads and a larger eye for a given body length than did those fish fed upon Mysis. We conclude that foraging anatomy in Arctic charr is phenotypically plastic and that variation in foraging behaviour that results in feeding specialization in the wild could induce variation in head anatomy. This in turn could reinforce foraging specialization. Very rapid epigenetic divergence into distinct feeding morphs (as demonstrated here) would allow selection to act at more than one mode and thus could promote rapid evolutionary divergence, initially prior to genetic segregation, in species which are highly plastic. (C) 2003 The Linnean Society of London, Biological Journal of the Linnean Society, 2003, 78, 43-49.", 
"In gnathostomes, the adenohypophysis, a component of the hypothalamo-hypophysial complex, is believed to develop through hierarchically organized epigenetic interactions based primarily on the topographical relationships between tissues. From a comparison of developmental processes and gene expression patterns of pituitary-related genes between the agnathan species, lampreys and gnathostomes, we speculate on the evolutionary pathway of the vertebrate adenohypophysis. In the lamprey, this is derived from the nasohypophysial placode (NHP) that develops anterior to the oral ectoderm. The NHP can be identified by the expression of LjPitxA, before actual histogenesis, but it is initially distant from the future hypothalamic region. Subsequently, the NHP expresses both LjFgf8/17 and LjBmp2/4a gene transcripts, and grows caudally to establish a de novo contact with the hypothalamic region by the mid-pharyngula stage. Later, the NHP gives rise to both the adenohypophysis and an unpaired nasal organ. Thus, the topographical relationship between the NHP and the hypothalamic region is established secondarily in the lamprey, unlike gnathostomes in which the equivalent relationship appears early in development. Comparing the developmental pattern of the amphioxus homologue of the adenohypophysis, we hypothesize that a modification of the regulation of the growth factor encoding gene lies behind the evolutionary changes recognized as heterochrony and heterotopy, which leads to the gnathostome hypophysial developmental pattern. (C) 2003, Wiley-Liss, Inc.", 
"In mammals and birds the genetic constitution established at the time of fertilization determines the type of gonad that develops, whereas in all crocodilians and many turtles it is the temperature experienced during the mid-trimester of embryogenesis that initiates gonadal differentiation. Research with the red-eared slider suggests considerable conservation in the genetic cascades that underlie the sex determination process in vertebrates and, further, that the patterns of expression of these genes appear to reflect phylogenetic relationships, with turtles being more similar to mammals than they are to birds and crocodilians. After the determination and differentiation of an individual's gonadal sex, epigenetic forces shape those morphological, physiological, and behavioral traits that characterize each individual's unique sexuality. Research with the leopard gecko thus relates to the fundamental question of what factors determine individual variability, particularly as it relates to sexually dimorphic behaviors. Taken together, this research illustrates how sexuality depends on sex, but sex should not be confused with sexuality. That is, sex is merely a means of categorizing individuals or gonads, whereas sexuality serves as a descriptor of concordant traits each of which is typically sexually dimorphic in its expression.", 
"Saccharomyces cerevisiae's ability to form the prion [PSI+] may increase the rate of evolvability, defined as the rate of appearance of heritable and potentially adaptive phenotypic variants. The increase in evolvability occurs when the appearance of the prion causes read-through translation and reveals hidden variation in untranslated regions. Eventually the portion of the phenotypic variation that is adaptive loses its dependence on the revealing mechanism. The mechanism is reversible, so the restoration of normal translation termination conceals the revealed deleterious variation, leaving the yeast without a permanent handicap. Given that the ability to form [PSI+] is known to be fixed and conserved in yeast, we construct a mathematical model to calculate whether this ability is more likely to have become fixed due to chance alone or due to its evolvability characteristics. We find that evolvability is a more likely explanation, as long as environmental change makes partial read-through of stop codons adaptive at a frequency of at least once every million years.", 
"Arabidopsis is a model system not only for studying numerous aspects of plant biology, but also for understanding mechanisms of the rapid evolutionary process associated with genome duplication and polyploidization. Although in animals interspecific hybrids are often sterile and aneuploids are related to disease syndromes, both Arabidopsis autopolyploids and allopolyploids occur in nature and can be readily formed in the laboratory, providing an attractive system for comparing changes in gene expression and genome structure among relatively 'young' and 'established' or 'ancient' polyploids. Powerful reverse and forward genetics in Arabidopsis offer an exceptional means by which regulatory mechanisms of gene and genome duplication may be revealed. Moreover, the Arabidopsis genome is completely sequenced; both coding and non-coding sequences are available. We have developed spotted oligo-gene and chromosome microarrays using the complete Arabidopsis genome sequence. The oligo-gene microarray consists of -26 000 70-mer oligonucleotides that are designed from all annotated genes in Arabidopsis, and the chromosome microarray contains 1 kb genomic tiling fragments amplified from a chromosomal region or the complete sequence of chromosome 4. We have demonstrated the utility of microarrays for genome-wide analysis of changes in gene expression, genome organization and chromatin structure in Arabidopsis polyploids and related species. (C) 2004 The Linnean Society of London.", 
"Historically, interpretations of both biological and cultural change within the prehistoric Azapa Valley, northern Chile, have cited large-scale population movements, with replacement from complex societies located in the adjacent highlands to the east. Biological estimates of this change have traditionally relied upon biodistance estimates, using craniofacial measures of both deformed and nondeformed skulls. In order to evaluate whether large-scale prehistoric migrations occurred in the Azapa Valley, we examine biodistance results from non-metric cranial traits for eight mortuary samples that represent all time periods of prehistoric occupation of the valley. None of the mean measures of divergences (MMD) among mortuary samples examined by this study were significant. These results suggest biological continuity in the Azapa Valley during 5,000 years of prehistory, with nonsignificant gene flow during the late Middle Horizon (AD 750-1100) and Late Intermediate (AD 1100-1476) periods. Biodistance results also suggest endogamy within coastal and inland populations. The broader implications of these results are discussed. (C) 2004 Wiley-Liss, Inc.", 
"Why are there two sexes in certain species, instead of one hermaphroditic sex? Why are Y chromosomes shorter than X chromosomes, but only in certain lineages? I propose that differences between sexes are initially determined by differential methylation in nuclear DNA between females and males, driving Muller's ratchet. Methylation of promoters suppresses transcription, including loci coding for gamete production, thereby converting hermaphroditic individuals into females or males. Differential methylation of sex chromosomes suppresses recombination and increases mutation rate, thereby geometrically increasing the speed of Muller's ratchet. Higher mutability of methylated nucleotides plus loss of sex-determining function of previously methylated nucleotides provides selective pressure to excise these loci, resulting in shorter Y or W chromosomes. Derived lineages usually have more methylation than do ancestral ones, and hence have relatively shorter sex chromosomes. Methylation canalizes dioecy and degeneration of sex chromosomes. Latter stages of sex chromosome evolution may have occurred via other mechanisms, for example sexually antagonistic genes or chromosomal rearrangements. A few aberrant derived lineages lost most methylation, and their sex determination and sex chromosomes may have evolved via other means. Differential methylation provides a mechanism for early evolution of dioecy in anisogamous sexual diploid eukaryotes and of sex chromosomes in metazoans. (C) 2003 The Linnean Society of London.", 
"Efforts to test hypotheses about small-scale shifts in development (tinkering) that can only be observed in the fossil record pose many challenges. Here we use the origin of modern human craniofacial form to explore a series of analytical steps with which to propose and test evolutionary developmental hypotheses about the basic modules of evolutionary change. Using factor and geometric morphometric analyses of craniofacial variation in modern humans, fossil hominids, and chimpanzee crania, we identify several key shifts in integration (defined as patterns of covariation that result from interactions between components of a system) among units of the cranium that underlie the unique shape of the modern human cranium. The results indicate that facial retraction in modern humans is largely a product of three derived changes: a relatively longer anterior cranial base, a more flexed cranial base angle, and a relatively shorter upper face. By applying the Atchley-Hall model of morphogenesis, we show that these shifts are most likely the result of changes in epigenetic interactions between the cranial base and both the brain and the face. Changes in the size of the skeletal precursors to these regions may also have played some role. This kind of phenotype-to-genotype approach is a useful and important complement to more standard genotype-to-phenotype approaches, and may help to identify candidate genes involved in the origin of modern human craniofacial form. (C) 2004 Wiley-Liss, Inc.", 
"Epigenesis concerns the interactions through which the inherited potentials of the genome become actualized into an adult organism. In addition to epigenetic interactions occurring within the developing embryo, there are also critical epigenetic interactions occurring between the embryo and its environment. These interactions can determine the sex of the embryo, increase its fitness, or even be involved in the formation of particular organs. This essay will outline the history of environmental concerns in developmental biology and provide some reasons for the decline and resurgence of these ideas, and it will then focus on two areas that have recently gained much attention: predator-induced polyphenisms and developmental symbioses. Research in these two areas of interspecies cooperation in morphogenesis has profound implications for what we consider to be normal development and how we proceed to study it. Studies of predator-induced polyphenism have shown that soluble factors from predators can change the development of prey in specific ways. Prey has evolved mechanisms to sense compounds released from their predators and to use these chemical cues to change their development in ways that prevent predation. New techniques in molecular biology, especially polymerase chain reaction and microarray analysis, have shown that symbioses between embryos and bacteria are widespread and that animals may use bacterial cues to complete their development.", 
"Development is the process by which genotypes are transformed into phenotypes. Consequently, development determines the relationship between allelic and phenotypic variation in a population and, therefore, the patterns of quantitative genetic variation and covariation of traits. Understanding the developmental basis of quantitative traits may lead to insights into the origin and evolution of quantitative genetic variation, the evolutionary fate of populations, and, more generally, the relationship between development and evolution. Herein, we assume a hierarchical, modular structure of trait development and consider how epigenetic interactions among modules during ontogeny affect patterns of phenotypic and genetic variation. We explore two developmental models, one in which the epigenetic interactions between modules result in additive effects on character expression and a second model in which these epigenetic interactions produce nonadditive effects. Using a phenotype landscape approach, we show how changes in the developmental processes underlying phenotypic expression can alter the magnitude and pattern of quantitative genetic variation. Additive epigenetic effects influence genetic variances and covariances, but allow trait means to evolve independently of the genetic variances and covariances, so that phenotypic evolution can proceed without changing the genetic covariance structure that determines future evolutionary response. Nonadditive epigenetic effects, however, can lead to evolution of genetic variances and covariances as the mean phenotype evolves. Our model suggests that an understanding of multivariate evolution can be considerably enriched by knowledge of the mechanistic basis of character development.", 
"I have tried to unpack the polysemy of the word epigenetics by adopting a historical point of view and by focusing on the models that were proposed at the beginning of the 1960s to explain variations in gene Activity during cell differentiation and development. Most of the questions that were or are at the core of epigenetics were posed in this period. This was due to the fact that the regulatory models and their extension to the notion of the genetic program were proposed as genetic answers to the questions raised by Waddington when he defined epigenetics in the 1940s. Studies of DNA methylation and chromatin structure, which became increasingly important in the 1960s and 1970s, were seen as alternative explanations to the regulatory mechanisms that had been previously proposed. This historical detour shows that epigenetics cannot be defined per se, but only as an evolving opposition to the piecemeal, reductionist approach of genetics.", 
"Genetic assimilation occurs when an acquired trait loses dependency on its environmental trigger and becomes an inherited trait. According to the standard quantitative genetic model for genetic assimilation, the trait is determined by the contributions of multiple genes. Trait expression occurs at a lower threshold with the trigger. Selection for the trait in the presence of the trigger increases the frequency of the trait-determining alleles. Eventually these alleles become frequent enough to breach the higher threshold for expression in the absence of the trigger. This loss of dependence on the trigger signifies genetic assimilation. Here I show that genetic assimilation can occur in the absence of selection for the trait in an evolutionary simulation of a gene network model. This contradicts the prediction of the standard quantitative genetic model, but is consistent with an explanation in terms of the canalization heuristic.", 
"Insecticide treatment of the aphid Myzus persicae (Sulzer) has led to the evolution of several insecticide resistance mechanisms, including the detoxification of insecticides by elevated esterases. This results from amplification of one of two closely related esterase genes (E4 or FE4) with up to 80 copies in the most resistant aphids. The amplified E4 genes are at a single site linked to a chromosomal translocation and resistance can be unstable. Individuals within a clone lose their elevated esterase and resistant phenotype, a good example of 'clonal variation'. This loss of esterase is accompanied by a loss of the corresponding mRNA but the amplified genes are retained with no detectable sequence differences. However, the expressed E4 genes contain 5-methylcytosine, which is lost at the same time as the genes are turned off. This is in direct contrast with vertebrate genes where DNA methylation causes gene silencing, but it does suggest that the resistant phenotype in M. persicae is under epigenetic control. One hypothesis is that 5-methylcytosine in E4 genes facilitates expression by preventing the production of incorrectly initiated transcripts. It is interesting that we have never detected silencing of amplified FE4 genes, possibly because they are at multiple loci and therefore less likely to be subject to synchronous control. (C) 2003 The Linnean Society of London.", 
"The value of quantitative intracranial nonmetric variation is examined in the study of population relationships by using samples from populations originating from five major geographic regions: Australia (two populations), Africa, East Asia, Europe, and Polynesia. According to the nonspecificity hypothesis, there are no distinct large classes of genes affecting one group of attributes exclusively; thus intracranial nonmetric traits should compare with other osteologic data sets in addressing questions of population relationships. By using the mean measure of divergence, intracranial nonmetric traits are shown to be useful in separating populations, particularly when using female and pooled-sex samples. The two Australian female samples (New South Wales coastal Australian and South Australian Aboriginals) are shown to be closer than any other two samples. The picture of intrapopulation and interpopulation variation in intracranial nonmetric traits is extended and clarified. Distance studies with intracranial nonmetric traits are possible but more illuminating if the sexes are first separated. Intracranial nonmetric variation does extend the knowledge of human population studies in yielding biologically meaningful results relating to development and ontogeny. (C) 2000 Wiley-Liss, Inc.", 
"What counts as epigenetic depends on what counts as genetic. It is argued that Weismannism, the doctrine of genetic continuity and somatic discontinuity, is the basis for an overly inclusive concept of epigenetics as every inherited resource beyond the genes. An alternative theoretical perspective, the reproducer concept, is introduced to facilitate analysis of multiple inheritance systems without labeling all nongenetic inheritance epigenetic..", 
"Given the quantity of molecular data now available, including complete genomes for some organisms. one can ask whether there is a need for any data beyond complete genomic sequences for phylogenetic analysis. One reason to look beyond the genome is that not all character information is encoded in organismal genomes. We propose a hierarchy of characters that ranges from biologically transmitted but nongenomically encoded characters, such as bird songs, to characters that are genomically encoded. All of these characters can retain historical information and are potentially useful for phylogenetic analysis. In addition, a number of phenotypic levels that are expressions of the genome can be identified. The question whether it is worth including any of these levels if all of the underlying sequence data have been collected arises, since issues of redundancy occur. Utilization of phenotypic levels that are ultimately based on sequences may facilitate reconstructing homologies that are not evident from sequence data alone. We propose the use of simultaneous analysis of sequence data and as many levels of phenotypic characters as possible to take advantage of homology information that may be more easily recovered from the latter. A method that eliminates redundancy to the degree that it can be detected is proposed. (C) 2003 The Willi Hennig Society. Published by Elsevier Inc. All rights reserved.", 
"In this paper, it is argued that differences in how one relates the genome to its surrounding contexts leads to diverse interpretations of the term epigenetics. Three different approaches are considered, ranging from gene-centrism, over gene-regulation, to dynamic systems approaches. Although epigenetics receives its widest interpretation in a systems approach, a paradigmatic shift has taken place in biology from the abandonment of a gene-centric position on to the present. The epistemological and ontological consequences of this shift are made explicit.", 
"To understand the evolution of Fot1, a member of the pogo family widely dispersed in ascomycetes, we have performed a phylogenetic survey across the genus Fusarium divided into six sections, The taxonomic distribution of Fot1 is not homogeneous but patchy; it is prevalent in the Fusarium oxysporum complex. absent in closely related sections, and found in five species from the most distant section Martiella. Multiple copies of Fot1 were sequenced from each strain in which the element occurs. In three species. the Fot1 nucleotide sequence is 98% identical to that from F. oxysporum (Fox), whereas nucleotide divergence for host genes is markedly higher: 11% for partial nuclear 28S rDNA and up to 30% for the gene encoding nitrate reductase (nia). In two species, sequence divergence of Fot1-related elements relative to Fox ranged from 7% to 23% (16% average). Most of the sequence differences (82%) were C-to-T and G-to-A transitions. These mutations are distributed throughout the Fot1 sequences, although they tend to be concentrated in the middle portion of the elements. Analysis of the local sequence context of transitions revealed a hierarchy of site preferences. These characteristics are typical of the repeat-induced point mutation process. first discovered in Neurospora crassa. The spotty distribution of Fot1 elements among species together with the high degree of similarity between Fot1 sequences present in distant species strongly suggests a case of horizontal transfer.", 
"In rainbow trout (Oncorhynchus mykiss), the acknowledged sex-determining system is genetic sex determination (GSD) with female homogamety (female XX-male XY). Subsequently, mitotic gynogens are all expected to be females. Unexpected maleness was fortuitously observed in a mitotic gynogenetic family of rainbow trout (13 males out of 27). An equal ratio of males and females suggested the possible segregation of some Mendelian sex-influencing factor. In order to perform a comprehensive analysis of the inheritance and expression of the factor involved, the transmission of maleness was studied across the next three generations, using both conventional and/or meiotic and mitotic gynogenetic offspring. On the whole, males as well as intersexes were observed in crosses between two expected carrier parents, and in gynogenetic offspring of expected carrier females, but not in crosses between one expected carrier parent and one normal XX control. Sex ratios in the different crosses often fitted Mendelian proportions, but not always. Both excess and lack of maleness were observed. The simplest hypothesis consistent with most results is a one-locus model, assuming the existence of a mutation (termed man of a sex-determining gene, which is able to override the primary XX mechanism of sex determination and to induce the development of testicular tissue in the gonads of expected XX individuals. The one-locus model requires that the mal mutation usually, but not systematically, behave as a recessive mutation and have a limited penetrance, that is, heterozygous (mal/+) may be sex reversed, homozygous (mal/mal may remain female, and carrier individuals may undergo partial masculinization alone (many intersexes were recorded). Inconsistency in sex ratios among offspring of parents expected to respond the same way was recorded, indicating that other modifier loci may also be involved. Finally, the occurrence of both males and females in clonal progenies showed that epigenetic factors also likely influence the expression of maleness. The effects of the mal mutation are compared to similar mutations recently described in other fish species. The nature and location of the mal gene (carried by heterochromosomes or an autosomal pair) is briefly discussed in view of the knowledge recently acquired on the subject.", 
"This volume deals with the role of epigenetics in life and evolution. The most dynamic forms of functional genome formatting involve DNA interacting with cellular complexes that do not alter sequence information. Such important epigenetic phenomena are the main subjects of other articles in this volume. This article focuses on the long-lived form of genome formatting that lies within the DNA sequence itself. I argue for a computational view of genome function as the long-term information storage organelle of each cell. Structural formatting consists of organizing various signals and coding sequences into computationally ready systems facilitating genome expression and genome transmission. The basic features of genome organization can be understood by examining the E. coli lac operon as a paradigmatic genomic system. Multiple systems are connected through distributed signals and repetitive DNA to form higher-order genome system architectures. Molecular discoveries about mechanisms of DNA restructuring show that cells possess the natural genetic engineering functions necessary for evolutionary change by rearranging genomic components and reorganizing system architectures. The concepts of cellular computation and decision-making, genome system architecture, and natural genetic engineering combine to provide a new way of framing evolutionary theories and understanding genome sequence information.", 
"The modified base 5-methylcytosine (C-m) plays an important functional role in the biology of mammals as an epigenetic modification and appears to exert a striking impact on the molecular evolution of mammal genomes. The collective epigenetic functions of C-m revolve around its effect on gene transcription, while the influence of this modified base on the evolution of mammal genomes derives from the greatly elevated spontaneous mutation rate of C-m to T. In mammals, C-m occurs at the dinucleotides CpG, CpA, and CpT. As a step toward a comprehensive statistical examination of the role of C-m in mammal molecular evolution, we have developed novel Markov models of codon substitution that incorporate dinucleotide-level terms relevant to C-m mutation. We apply these models to two data sets of aligned BRCA1 exon 11 sequences from bats and primates. In all cases, terms specific to mutations that affect the dinucleotides CpG, CpA, and CpT significantly improved model fit. For the CpG-specific terms, both transition and transversion substitution rates were elevated. These rates differed between the data sets. Bats exhibited a lower relative rate of substitutions at CpG-containing codons. Transition substitutions were significantly less than 1 at CpA-containing codons but greater than 1 at CpT-containing codons. The inclusion of interaction terms in the codon models to represent possible confounding with the effect of natural selection were supported for codons that contained CpG and CpT, but not CpA. From the results, we infer that mutation of C-m is a probable factor that affects BRCA1 codons containing the dinucleotide CpG, a possible factor for CpA-containing codons, and an unlikely factor that affects CpT-containing codons. The confounding of estimated terms with the effect of natural selection indicate this confounding must be addressed for comparisons between different coding and noncoding regions.", 
"Repetitive DNA sequences comprise a substantial portion of most eukaryotic and some prokaryotic chromosomes. Despite nearly forty years of research, the functions of various sequence families as a whole and their monomer units remain largely unknown. The inability to map specific functional roles onto many repetitive DNA elements (RIES), coupled with the taxon-specificity of sequence families, have led many to speculate that these genomic components are selfish replicators generating genomic junk. The purpose of this paper is to critically examine the selfishness, evolutionary effects, and functionality of REs. First, a brief overview of the range of ideas pertaining to RE function is presented. Second, the argument is presented that the selfish DNA hypothesis is actually a narrative scheme, that it serves to protect neo-Darwinian assumptions from criticism, and that this story is untestable and therefore not a hypothesis. Third, attempts to synthesize the selfish DNA concept with complex systems models of the genome and RE functionality are critiqued. Fourth, the supposed connection between RE-induced mutations and macro-evolutionary events are stated to be at variance with empirical evidence and theoretical considerations. Hypotheses that base phylogenetic transitions in repetitive sequence changes thus remain speculative. Fifth and finally, the case is made for viewing RIES as integrally functional components of chromosomes, genomes, and cells. It is argued throughout that a new conceptual framework is needed for understanding the roles of repetitive DNA in genomic/epigenetic systems, and that neo-Darwinian narratives have been the primary obstacle to elucidating the effects of these enigmatic components of chromosomes.", 
"Documentation of variation in phalangeal formulae in land tortoises combined with ontogenetic information from turtles in general were used, in a phylogenetic context, to infer the potential effect of size and developmental constraints upon patterns of morphological variation. A sample of 201 specimens and published illustrations of 37 tortoise species were examined, representing all but one living genera and most species of the Testudinidae. Specimens were either articulated dry skeletons or preserved animals that were x-rayed. The patterns of digital and phalangeal loss in tortoises were predicted from developmental studies of the manus and pes in other turtles. If a digit is lost, it is the first digit, which is the last one to develop. If a digit has a single phalanx, it is usually the fifth digit. The primitive phalangeal formula for land tortoises is probably 2-2-2-2-1, the most common pattern found in living testudinid species. The presence of a second phalanx in the fifth digit evolved independently many times and usually in large tortoises. Such additions were interpreted as instances of peramorphosis. Many small tortoises have a full complement of digits (five) and phalanges (two in each digit); nevertheless, phalangeal and digital loss is associated with small size. Small and medium size tortoises exhibit greater variation in phalangeal number than do large tortoises. We hypothesize that epigenetic processes, and not simply adaptation, played a major role in the evolution of the variation in phalangeal formulae in tortoises. J. Exp. Zool. (Mol. Dev. Evol.) 302B:134-146, 2004. K, 2004 (C) Wiley-Liss, Inc.", 
"In current biological and philosophical literature, the use of the terms epigenesis and epigenetics has increased tremendously. As these terms are often confused, this paper aims at clarifying the distinction between them by drawing their conceptual and historical evolutions. The evolution of the term epigenesis is situated in the context of early embryological studies. Departing from Aristotle's natural philosophy, it is shown that epigenesis gained alternating attention from the 17th century onwards, as it was introduced into neo-classical embryology and considered to be the opposite of the preformationist tradition. Where preformation stated that the germ cells of each organism contain preformed miniature adults that unfold during development, epigenesis held that the embryo forms by successive gradual exchanges in an amorphous zygote. Although both traditions tried to explain developmental organization, religious and metaphysical arguments on the conception of embryonic matter as either active or passive determined the scope of their respective explanations. It is shown that these very arguments still underlie the use of gene-centric metaphors in the molecular revolution of the 20th century.", 
"Polyploidization has occurred often in the evolutionary history of eukaryotes, yet we are only now learning about the genetic and epigenetic events that occur in newly formed polyploids. A long-standing assumption has been that each member of a gene pair would contribute equally to expression levels after polyploidization. This assumption has now been shown to be false in cottons. Adams et al. studied expression levels in different plant tissues from a newly formed allotetraploid cotton (bearing two copies of the so-called 'A' genome and two copies of the 'D' genome). The authors found that the proportion of mRNA levels transcribed from the A and D genomes varied dramatically among tissues. This result implies that duplicated genes can undergo an immediate divergence in function as a pleiotropic effect of hybridization or polyploidization, providing a novel explanation for why selection often preserves duplicated genes.", 
"Endogenous pararetroviruses (EPRVs) represent a new class of dispersed repetitive DNA in plants. The genomes of many Nicotiana species and other solanaceous plants are rich in EPRVs. Distinct EPRV families are present in N. sylvestris (Ns) and in N. tomentosiformis (Nto), the two diploid progenitors of allotetraploid N. tabacum. Nicotiana EPRVs represent an interesting type of repetitive sequence to analyse in polyploids because of their potential impact on plant fitness and the epigenetic architecture of plant genomes. The NsEPRV family appears identical in N. sylvestris and N. tabacum, indicating little change has occurred in either species since polyploid formation. By contrast, the NtoEPRV family is larger in N. tomentosiformis than in N. tabacum, suggesting either preferential elimination from the polyploid genome or specific accumulation in the diploid genome following polyploidization. The lability of NtoEPRVs might be enhanced by a frequent association with gypsy retrotransposons. Although some EPRVs are probably benign, others are potentially pathogenic or, conversely, determinants of virus resistance. Normally quiescent EPRVs can be reactivated and cause symptoms of infection in hybrids of species that differ in their EPRV content. EPRVs that furnish immunity to the free virus exemplify the selective value of so-called 'junk' DNA. Variation in the abundance and distribution of EPRVs among related species can be useful in taxonomic and evolutionary studies. (C) 2004 The Linnean Society of London.", 
"Interspecific hybridization in the rodent genera Peromyscus and Mus results in abnormal placentation. In the Peromyscus interspecies hybrids, abnormal allelic interaction between an X-linked locus and the imprinted paternally expressed Peg3 locus was shown to cause the placental defects. In addition, loss-of-imprinting (LOI) of Peg3 was positively correlated with increased placental size. As in extreme cases this placental dysplasia constitutes a post-zygotic barrier against interspecies hybridization, this finding was the first direct proof that imprinted genes may be important in speciation and thus in evolution. In the Mus interspecies hybrids, a strong role of an X-linked locus in placental dysplasia has also been detected. However, here we show by backcross and allele specific expression analyses that neither LOI of Peg3 nor abnormal interactions between Peg3 and an X-linked locus are involved in generating placental dysplasia in Mus hybrids, although the placental phenotypes observed in the two genera seem to be identical. In contrast to this, another dysgenesis effect common to Peromyscus and Mus hybrids, altered foetal growth, is caused at least in part by the same X-chromosomal regions in both genera. These findings first underline the strong involvement of the X-chromosome in the genetics of speciation. Secondly, they indicate that disruption of epigenetic states, such as LOI, at specific loci may be involved in hybrid dysgenesis effects in one group, but not in another. Thus, we conclude that even in closely related groups divergent molecular mechanisms may be involved in the production of phenotypically similar post-zygotic barriers against hybridization.", 
"Generally speaking, epigenetic states or epigenetic regulation refer to situations in which several states of gene,expression may coexist in similar environmental conditions, despite the absence of significant changes in the genomic sequence. In one way or another, the mechanisms behind these phenomena involve vicious circles, so that each epigenetic. state tends to sustain itself, even after the disappearance of the inductive signal involved in the selection of that particular state. These vicious circles constitute positive feedback circuits and are found at the core of many developmental regulatory systems. In this paper, we present a qualitative model for the regulatory network formed by maternal and gap gene crossregulations. This network controls the initial anterior-posterior patterning during early Drosophila embryogenesis and encompasses several intertwined feedback circuits. On the basis of our model analysis, we derive interesting insights about how specific expression states of the gap genes are selected along the anterior-posterior axis, in particular in relation with the activity of one positive feedback circuit, namely that formed by giant and Kruppel cross-inhibitions. In addition, we are able to qualitatively simulate the patterns of gene expression in the wild-type, as well as to predict the phenotypes of various loss-of-function mutations at the maternal and gap genes, or cis-regulatory mutations at the gap genes, as well as the effects of ectopic expression of these genes.", 
"The Tetrahymena group I ribozyme catalyzes the cleavage of a phosphodiester linkage in specific sequences of RNA. This phenotype can be used in an in vitro selection-amplification process to evolve variants that are capable of RNA catalysis in the presence of Ca2+ as the sole available cation. With sufficient genotypic characterization of the population as it evolves, we have a rare opportunity of observing how the information stored in an evolving population responds to selective pressures, such as the requisite of catalyzing RNA cleavage in the absence of Mg2+ or Mn2+. In the present work, we examine the population dynamics of this system using sequence information from previous experimental work. We focus on two issues: How does the information content of the population evolve? and Is the system evolving as an adaptive walk on a rugged landscape? To investigate these questions, information theoretical parameters are examined. The evolution of the population is visualized by mapping the genotypic frequency distribution onto a two-dimensional projection of sequence space. The projection was generated using Hamming distances from the wild-type, starting sequence and a catalytically successful, evolved sequence. The evolution of the information content of the system was measured by calculating the grammar complexity of the observed sequences, which showed a very slight increase over 12 generations. This result is consistent with the system performing a search for a local optimum. The dynamics of the population in this sequence space is consistent with an adaptive walk on an uncorrelated, or rugged, genotypic landscape, despite the observation that the phenotypic progress of the population appears smooth. The relative insensitivity of the phenotypic landscape to the variegation of the genotypic landscape suggests that the former is buffered against variation in the latter through various epigenetic-like mechanisms.", 
"A subset of autosomal genes undergo genomic imprinting which results in expression from only the paternal or maternal chromosome. While this phenomenon is restricted to mammals and angiosperms, the underlying silencing mechanisms appear to be evolutionarily conserved. A biallelically unmethylated DNaseI hypersensitive region (A6-A4) between the imprinted Igf2 and H19 genes is conserved in humans and mice and functions as a tissue-specific maintenance element for the imprinted growth factor IGF2. In order to analyse A6-A4 for potentially conserved transcriptional maintenance properties, we have generated transgenic Drosophila harbouring the element in a reporter construct. These flies depicted silencing of the reporter genes lacZ and mini-white. The silenced state of the mini-white gene showed variegation and sensitivity to temperature changes. In addition, two members of the conserved Polycomb group, Enhancer of zeste and Posterior sex combs, were needed for repression. Polycomb group proteins are essential for gene silencing during development. Our results indicate that Polycomb group proteins may also be involved in the regulation of mammalian imprinted genes.", 
"Developmental stability (DS) may confer an advantage in competition for mates. The present study tests this hypothesis using Drosophila immigrans, and proposes a novel approach to help broadly define the epigenetic factors causing such an effect. We first estimated the magnitude of isofemale heritability in sternopleural bristle fluctuating asymmetry (FA), using replicate genetic lines extracted from nature. Positional FA (PFA) exhibited significant among-line variation, and the heritability estimate of 0.10 (0.046 s.e.m.) was statistically significant. Among individual males, there was a significant positive relationship between PFA and copulation latency (time elapsed between introduction of females and copulation) and duration, but not copulation frequency. Moreover, high-DS lines exhibited significantly shorter copulation latency and duration compared with low-DS lines. When these components of sexual performance were again contrasted between lines with among-individual differences in bristle asymmetry controlled statistically, significant line effects on copulation latency and duration disappeared. The results suggest that deficits in the developmental apparatus underlying one particular trait can compromise individual sexual performance, and weaken the hypothesis that FA is a cue of overall 'genetic quality'.", 
"It is well known that repositioning of a gene often exerts a strong impact on its own expression and whole development. Here we report the results of genome-wide analyses suggesting that repositioning may also radically change the evolutionary fate of gene duplicates. As an indicator of these changes, we used the GC content of gene pairs which originated by duplication. This indicator turned out to be duplicate-asymmetric, which means that genes in a pair differ significantly in GC content despite their apparent origin from a common ancestor. Such an asymmetry necessarily implies that after duplication two originally identical genes mutated in opposite directions-toward GC-rich and GC-poor content, respectively. In mammalian genomes, this trend is definitely associated with presumably methylated hypermutable CpG sites, and in a typical GC-asymmetric gene pair, its two member genes are embedded in GC-contrasting isochores. However, we unexpectedly found similar significant GC asymmetry in fish, fly, worm, and yeast. This means that neither methylation alone nor methylation in combination with isochores can be counted as a primary cause of the GC asymmetry; rather they represent specific realizations of some universal principle of genome evolution. Remarkably, genes from pairs with the greatest GC asymmetry tend to be on different chromosomes, suggesting that the mutational difference between gene duplicates is associated with translocation of a new gene to a different place in the genome, whereas GC symmetric pairs demonstrate the opposite tendency. A recently emerged extra gene copy is usually on the same chromosome as is its parent but quickly, by 0.05 substitution per synonymous site, either has perished or occupies a different chromosome. During this earliest posttranslocation period, the ratio of nonsynonymous/synonymous base substitutions is unusually high, suggesting a rapid adaptive evolution of novel functions. In a general context of evolution by gene duplication, our interpretation of this position-dependent GC asymmetry between duplicated genes is that evolution of redundant genes toward a new function has often been associated with their very early, postduplication repositioning in the genome, with a concomitant abrupt change in epigenetic control of tissue/stage-specific expression and an increase in the mutation rate. Of eight eukaryotic genomes studied, the most distinguished in this respect is the human genome.", 
"The complexity of some sexual reproductive systems in arthropods still leaves both their genetic and epigenetic determinism and their evolutionary significance poorly understood. Pseudoarrhenotoky is characterized by obligate fertilization and differential inactivation and/or elimination of paternal chromosomes in embryos that develop into males. Here, we investigate how the paternal genome is transmitted in a pseudoarrhenotokous mite, Neoseiulus californicus, using codominant genetic markers detected by DALP (direct amplification of length polymorphism). Transmission patterns of parental alleles through one and two generations are reported at four or five loci corresponding to four linkage groups. Our data provide strong evidence for selective elimination of the paternal genome among male tissues. Sperm contained maternal genes exclusively, whereas some male somatic tissues retained most if not all paternal chromosomes. No recombination between parental genomes prior to paternal genome elimination from the embryonic germ line was observed. These data allow a reinterpretation of previous phenotypic and cytogenetic observations in these mites, from which we suggest some relevant mechanistic and evolutionary implications. In addition, this is the first published study using polymorphic codominant loci detected by the recently developed DALP method.", 
"During the development of a multicellular organism from a zygote, a large number of epigenetic interactions take place on every level of suborganismal organization. This raises the possibility that the system of epigenetic interactions may compensate or ''buffer'' some of the changes that occur as mutations on its lowest levels, and thus stabilize the phenotype with respect to mutations. This hypothetical phenomenon will be called ''epigenetic stability.'' Its potential importance stems from the fact that phenotypic variation with a genetic basis is an essential prerequisite for evolution. Thus, variation in epigenetic stability might profoundly affect attainable rates of evolution. While representing a systemic property of a developmental system, epigenetic stability might itself be genetically determined and thus be subject to evolutionary change, Whether or not this is the case should ideally be answered directly, that is, by experimentation. The time seals involved and our insufficient quantitative understanding of developmental pathways will probably preclude such an approach in the foreseeable future. Preliminary answers are sought here by using a biochemically motivated model of a small bur central part of a developmental pathway. Modeled are sets of transcriptional regulators that mutually regulate each other's expression and thereby form stable gene expression patterns. Such gene-expression patterns, crucially involved in determining developmental pattern formation events, are most likely subject to strong stabilizing natural selection, After long periods of stabilizing selection. the fraction of mutations causing changes in gene-expression pattern is substantially reduced in the model. Epigenetic stability has increased. This phenomenon is found for widely varying regulatory scenarios among transcription factor genes. Its discussed that only epistatic (nonlinear) gene interactions can cause such change in epigenetic stability. Evidence from paleontology, molecular evolution, development, and genetics, consistent with the existence of variation in epigenetic stability, is discussed, The relation of epigenetic stability to developmental canalization is outlined. Experimental scenarios at suggested thar may provide further evidence.", 
"Expression of imprinted genes is dependent on their parental origin. This is reflected in the heritable differential methylation of parental alleles. The gametic imprints are however reversible as they do not endure for more than one generation. To investigate if the epigenetic changes in male and female germ line are similar or not, we derived embryonic germ (EG) cells from primordial germ cells (PGCs) of day 11.5 and 12.5 male and female embryos. The results demonstrate that they have an equivalent epigenotype. First, chimeras made with EG cells derived from both male and female embryos showed comparable fetal overgrowth and skeletal abnormalities, which are similar to but less severe than those induced by androgenetic embryonic stem (ES) cells. Thus, EG cells derived from female embryos resemble androgenetic ES cells more than parthenogenetic cells. Furthermore, the methylation status of both alleles of a number of loci in EG cells was similar to that of the paternal allele in normal somatic cells. Hence, both alleles of Igf2r region 2, Peg1/Mest, Peg3, Nnat were consistently unmethylated in EG cells as well as in the primary embryonic fibroblasts (PEFs) rescued from chimeras. More strikingly, both alleles of p57kip2 that were also unmethylated in EG cells, underwent de novo methylation in PEFs to resemble a paternal allele in somatic cells. The exceptions were the H19 and Igf2 genes that retained the methylation pattern in PEFs as seen in normal somatic tissues. These studies suggest that the initial epigenetic changes in germ cells of male and female embryos are similar.", 
"Many insects are attacked by internal parasitoids against which they mount a largely cellular immunological defense. The resistance of a host and the virulence of a parasitoid determine which species survives after parasitism. Drosophila is parasitized by several hymenopterous parasitoids, especially those in the genera Asobara and Leptopilina. Geographic patterns have been found in parasitoid virulence and host resistance, the dearest of which is a dine in Asobara tabida virulence from the north (low) to the south thigh) of Europe. Drosophila melanogaster resistance is highest in central-southern Europe and lower elsewhere. We review and interpret these patterns in the light of recent experimental and theoretical studies of the evolution and coevolution of these traits. We find no evidence for genotype-specific virulence and defense, which makes Red Queen-type coevolution unlikely. The most important explanation for the patterns is geographic differences in host-parasitoid community structure. Asobara tabida virulence is positively correlated with the resistance of its main hosts, and there is more limited evidence that D. melanogaster resistance is influenced by the virulence of its parasitoids. We critically appraise whether the evidence available so far supports a coevolutionary explanation for the levels of these trails.", 
"We discuss the role of cell memory in heredity and evolution. We describe the properties of the epigenetic inheritance systems (EISs) that underlie cell memory and enable environmentally and developmentally induced cell phenotypes to be transmitted in cell lineages, and argue that transgenerational epigenetic inheritance is an important and neglected part of heredity. By looking at the part EISs have played in the evolution of multicellularity, ontogeny, chromosome organization, and the origin of some post-mating isolating mechanisms, we show how considering the role of epigenetic inheritance can sometimes shed light on major evolutionary processes.", 
"Cytosine methylation is widely distributed in multicellular organisms. We present a comprehensive survey of the existing data on the phylogenetic distribution of DNA methylation in invertebrates, together with new data for the crustacean Penaeus semisulcatus, the annelid Aporrectodea caliginosa trapezoides, and the parasitic platyhelminth Schistosoma mansoni. Two alternative hypotheses addressing the function of cytosine methylation in invertebrates are evaluated: (1) cytosine methylation is an ancient regulatory mechanism which was lost in species with low rates of cell turnover, and (2) cytosine methylation is primarily a defense mechanism against genomic parasites and is expected to be present in all species with large genomes. We discuss the role of DNA methylation in the evolution of development in light of these hypotheses and conclude that gene control and cell memory are important and primitive functions of DNA methylation.", 
"Redundant gene functions are ubiquitous, and they are a potentially important source of evolutionary innovations on the biochemical level. It is therefore highly desirable to understand the mechanisms governing their evolution. Gene duplication is clearly a prominent mechanism generating redundant genes. However, because redundancy provides a protective effect against deleterious mutations, natural selection might be involved in generating and maintaining partial redundancy. Although much experimental data on redundant genes have accumulated, no data are available that could elucidate what role selection has in their evolution. As a first step towards answering this question, a conceptually simple mathematical model for the evolution of redundancy is introduced. its main result is that selection cannot only maintain but also increase redundancy among genes in a population provided (i) that mutation generates sufficient variation in redundancy and (ii) that populations are large. The population biological process at work is somewhat unusual. Selection does not act on the (nonexisting) differential fitness between individuals with different degrees of redundancy. Rather, it acts through the low number of offspring with deleterious mutations that individuals with redundant genes will generate. Moreover, even if populations are small and variation in redundancy is low, selection will substantially slow the 'decay' of redundancy caused by mutation and genetic drift. Methodological problems in determining degrees of redundancy experimentally are discussed, as well as issues concerning the relation of redundancy to genetic canalization. The latter two phenomena necessitate a differentiated view of neutral mutations, where some neutral mutations are only neutral because their effects on gene products are absorbed by the epigenetic system.", 
"Since the Modern Synthesis, evolutionary biologists have assumed that the genetic system is the sole provider of heritable variation, and that the generation of heritable variation is largely independent of environmental changes, However, adaptive mutation, epigenetic inheritance, behavioural inheritance through social learning, and language-based information transmission have properties that allow the inheritance of induced or learnt characters. The role of induced heritable variation in evolution therefore needs to be reconsidered, and the evolution of the systems that produce induced variation needs to be studied.", 
"Three different human femoro-tibial characters are selected as functionally relevant and derived hominid characters: femoral bicondylar angle, shape of the femoral distal epiphysis, and the tibial insertion of the lateral meniscus. The timing and mode of formation of these characters are investigated during human ontogeny and are shown to differ considerably. The available hominid fossils (Australopithecus afarensis and early Homo) are interpreted in the light of this ontogenetic analysis with the conclusion that, during hominid evolution, different modes of selection of these features must have occurred. In modern humans, the femoral bicondylar angle proves to be an epigenetic functional feature, which develops during early childhood growth. It is present in all australopithecines and we suggest that it developed following a change in their locomotor behavior and not upon a genomic change: the early practice of bipedal walking, with adducted knee joints, in the locomotor repertoire of infant australopithecines, was sufficient to promote this angle. Later in hominid evolution, the knee joint evolved from having a single insertion of the lateral meniscus on the tibia to a double one. While Australopithecus afarensis exhibits a single insertion, early Homo clearly exhibits a double insertion of the lateral meniscus on the tibia. The double insertion restricts the mobility of the meniscus on the tibial plateau, indicating a habitual practice of full extension movements of the knee joint. Among modern humans, the posterior insertion of the lateral meniscus appears early in fetal life. Consequently in early Homo, this new selected feature developed directly as a result of a genomic change. The derived shape of human distal femoral epiphysis includes a prominence of the lateral lip of the femoral trochlea, an elliptical profile of the lateral condyle, and an anteroposterior lengthening of the epiphysis. Analysis of human fetal and neonatal distal epiphyses shows that the prominence of the lateral lip of the trochlea arises before any use, and thus appears to be genetically determined. However, the postnatal development of this joint shows that this feature is also modified epigenetically by use. It is argued that the hominid femoropatellar joint would have been reshaped following the process of genetic assimilation (Waddington [1942] Nature 3811:563-565). The prominence of the lateral lip of the femoral trochlea was probably selected following a two-staged process-first epigenetic, then genetic. Far from being a Lamarckian explanation, this concept applies precisely to adaptive characters that are induced by an external stimulus during a single lifetime and are replaced through natural selection by genetically based equivalent characters. The nature of the structures involved in the studied features is shown to be an important parameter determining their mode of development and selection. (C) 1999 Wiley-Liss, Inc.", 
"The adaptive value of epigenetic inheritance systems is investigated in a simple mathematical framework. These systems enable the environmentally induced phenotypes to be transmitted between generations. The frequencies of the different epigenetic variants are determined by the plasticity and the efficiency of transmission (called memory). Plasticity and memory are genetically determined. This paper studies the evolution of a quantitative character, its plasticity and memory, on the adaptive landscape. Due to the dual inheritance of the character, selection acts on two revels: on the phenotypes of the same genotype, and on the different genotypes. Plasticity generates the raw material, and memory increases the strength of phenotypic selection. If the character is far from the peak of the landscape, then dual inheritance of the character can be advantageous for the genotype. Near the peak it is more favourable to suppress phenotypic variation. This would lead to genetic assimilation.", 
"Evolutionary biologists are largely polarized in their approaches to integrating microevolutionary and macroevolutionary processes. Neo-Darwinians typically seek to identify population-level selective and genetic processes that culminate in macroevolutionary events. Epigeneticists and structuralists, on the other hand, emphasize developmental constraints on the action of natural selection, and highlight the role of epigenetic shifts in producing evolutionary change in morphology. Accordingly, the ways in which these paradigms view and address morphological contrasts between classes of related organisms differ. These paradigms, although seldomly explicitly stated, emerge in paleoanthropology as well. Considerations of postcranial morphological contrasts between archaic and modern humans typically fall into one of two broad interpretive models. The first derives from the neo-Darwinian perspective and holds that evolution in the postcranial skeleton was largely mosaic (operating in a particulate manner), and that temporal change in specific traits informs us about behavioral shifts or genetic evolution affecting isolated anatomical regions (i.e., adaptive behavioral inferences can be made from comparative studies of individual trait complexes). The alternative model follows from the epigeneticist paradigm and sees change in specific postcranial traits as correlated responses to change in overall body form (involving shifts in regulation of skeletal growth, or selective and developmental responses to broad adaptive shifts). By this view, ilztegration of functional systems both constrains and directs evolution of various traits, and morphological contrasts inform us about overall change in body form related to change in such things as overall growth patterns, climatic adaptation, and technological dependency. These models were tested by confirmatory factor analysis using measures of upper body form and upper limb morphological traits in Eurasian Neandertal and early modern fossils and recent human samples. Results indicate (1) a model of morphological integration fits the data better than a model of no integration, but (2) this integration accounts for less than half of the variance in upper limb traits, suggesting a high degree of tolerance for particulate evolution in the context of an integrated upper body plan. Significant relationships were detected between joint shapes and body size, between humeral shaft shape and body size and chest shape, and between measures of biomechanical efficiency and robusticity. The observed morphological differences between late archaic and early modern humans reflect particulate evolution in the context of constraints imposed by genetic and morphological integration. While particulate approaches to interpreting the fossil record appear to be justified, attention must also be paid to delineating the nature and extent of morphological integration and its role in both constraining and producing observed patterns of variation between groups. Confirmatory factor analysis provides a means of examining trait covariance matrices, and sert es as a useful method of identifying patterns of integration in morphology. (C) 1996 Wiley-Liss, Inc.", 
"Most traditional views of homology rely on two unwarranted premises: the pervasively hierarchical nature of biology, inclusive of the levels of genes, development, and morphology and the linear mapping of genes onto developmental schedules and of developmental schedules onto phenotypes. These premises are only occasionally verified. Hierarchical behavior is negated by gene duplication and exon shuffling at the level of genes, by the coexistence of autonomous vs nonautonomous gene expression at the level of development, by ontogenetic repatterning at the level of morphology. The linearity of mapping of genes onto development is disturbed by genetic piracy, uncoupling of positional vs spatial control, and pleiotropy. The independence of developmental modules affects the mapping of development onto morphology and, finally, the peculiar topology of the epigenetic code affects the linearity of the gene to phenotype mapping. To cope with this complex behavior, a combinatorial approach to homology is recommended, (C) 1998 Academic Press.", 
"The occurrence and distribution of 35 cranial epigenetic traits in the Italian Neandertals (Saccopastore 1 and 2, Gualtari 1) were examined according to morpho-functional cranial regions and with respect to a distinction between hypostosis (i.e., weak osseous development, arrested morphogenesis, retention of infantile features) and hyperostosis (i.e. excess of ossification, not reaching the pathological condition); The results, expressed as hypostotic scores, showed higher levels of hypostosis in these Neandertal specimens than in recent European samples. The highest expressions of hypostotis were observed in those regions of the Neandertal cranium where disequilibrium between skeletal and cerebral growth factors was expected. These results-interpreted as expression of developmental stress-are consistent with a heterochronic interpretation of the development of the Neandertal cranium; namely, a faster ossification of the cranial vault relative to brain growth rates. (C) 1996 Academic Press Limited.", 
"Six lines of flax (Linum usitatissimum) were derived from six short, early flowering plants that were first-generation progeny of plants grown from seeds treated with 5-azacytidine. The third and fourth progeny generations of the lines, and the F-1 and F-2 progeny of crosses between three of the lines and their corresponding untreated controls, demonstrated the relatively stable inheritance of the induced phenotypes and provided information on the genetic control of the induced changes, Some reversion of the induced phenotypes was detected, but much of the phenotypic variability observed in the progeny generations could be attributed to segregation, Segregation patterns demonstrated that the early flowering phenotype is determined by the combined effects of 5-azacytidine-induced changes at three (or more) independent loci, Furthermore, the induced form of one locus is dominant or codominant, but the induced forms of the other loci are recessive. A working model describes the proposed genetic control, and the significance of 5-azacytidine-induced effects which are recessive is discussed.", 
"Cortical maps often contain global spatial structure; however, theoretical accounts for their development have generally concentrated on reproducing only local structure. We show that the elastic net model of cortical map formation can closely approximate the global structure of the ocular dominance column map observed in macaque primary visual cortex. A key component is the assumption of spatially non-uniform and anisotropic correlations in the retina. This work shows how genetic and epigenetic effects could combine to establish characteristic global structure in cortical maps.", 
" ", 
" ", 
"Genomic imprinting results in the functional specialization of the maternal and paternal genomes during development whereby offspring inherit only one active copy of a gene. Although the reason for its evolutionary genesis remains speculative, the consequences of genomic imprinting are evidenced by the failure of parthenogenetic and androgenetic development in mammals, and parental-specific effects in the etiology of a number of human diseases, While the precise molecular mechanism of imprinting is unknown, evidence suggests that the specialization of the parental genomes is established during gametogenesis when the parental genomes are epigenetically modified to reflect the parent of origin, To examine the epigenetic modification of specific imprinted genes and subsequent differential expression, an assay is required that can distinguish between the maternal and paternal alleles and their respective transcripts, During the past 5 years several strategies have been used to identify imprinted genes, ranging from the fortuitous disruption of specific parental alleles to subtraction hybridization between cDNAs from normal and parthenogenetic embryos, To study the developmental regulation of these imprinted genes during mammalian development, we describe a relatively simple interspecies ''mRNA phenotyping'' approach applicable to the analysis of allele-specific expression as well as the identification of candidate imprinted genes.", 
"Because development is epigenetic, diverse aspects of morphology are integrated during ontogeny. Using the method of thin-plate splines, and the decomposition of these splines by their principal warps, we examine the ontogeny of integrated features of skull growth of the cotton rat, Sigmodon fulviventer as observed in landmark locations in the ventral view. Postnatal growth of the skull in Sigmodon is not adequately described by the familiar contrast between relatively rapid facial elongation and slow, precocial growth of the cranial base. No developmental units corresponding to facial skull and cranial base emerge from analysis of geometric shape change. Rather, skull growth is both more integrated and more complex, exhibiting both skull-wide integration and locally individualized regions. Like skull shape, integration has an ontogeny; different regions of the skull can be partitioned into developmentally individualized parts in different ways at different ages. The effective count of individualized parts decreases substantially before weaning occurs, suggesting that the integration required by the functionally demanding activity of chewing gradually develops before the functional transition occurs. Our description of skull growth and integration does not depend upon arbitrary a priori choices about what to measure; rather, we base our decomposition of the whole into parts upon results of the data analysis. Our approach complicates the study of heterochrony, but, because it expresses the spatiotemporal organization of ontogeny, it enables the study of heterotopy.", 
"Fluctuating asymmetry is an epigenetic measure of the ability of individuals to undergo identical development of a usually bilaterally symmetrical character on both sides of the body. Horns of beetles and spurs of birds are elaborate structures usually restricted to or enlarged in individuals of the limited sex and frequently used in intrasexual combat. Individuals with large horns usually win fights against individuals with small horns which suggests that horn size may reliable signal male fighting ability. A comparative study of the patterns of fluctuating asymmetry in horns of beetles and spurs of birds showed that the degree of asymmetry in these secondary sex traits was considerably larger than in elytra and wing length. which are apparently not subjected to sexual selection. There was a negative relationship between the degree of asymmetry and size of the secondary sex trait while the relationship for elytra and wing length was flat or U-shaped. This demonstrates that horn and spur size may reliable reflect male quality as determined by the degree of fluctuating asymmetry.", 
"Herein we describe a general multivariate quantitative genetic model that incorporates two potentially important developmental phenomena, maternal effects and epigenetic effects. Maternal and epigenetic effects are defined as partial regression coefficients and phenotypic variances are derived in terms of age-specific genetic and environmental variances. As a starting point, the traditional quantitative genetic model of additive gene effects and random environmental effects is cast in a developmental time framework. From this framework, we first extend a maternal effects model to include multiple developmental ages for the occurrence of maternal effects. An example of maternal effects occurring at multiple developmental ages is prenatal and postnatal maternal effects in mammals. Subsequently, a model of intrinsic and epigenetic effects in the absence of maternal effects is described. It is shown that genetic correlations can arise through epigenetic effects, and in the absence of other developmental effects, epigenetic effects are in general confounded with age-specific intrinsic genetic effects. Finally, the two effects are incorporated into the basic quantitative genetic model. For this more biologically realistic model combining maternal and epigenetic effects, it is shown that the phenotypic regressions of offspring on mother and offspring on father can be used in some cases to estimate simultaneously maternal effects and epigenetic effects.", 
"Fluctuating asymmetry occurs when an individual is unable to undergo identical development of an otherwise bilaterally symmetric trait on both sides of its body. Since both sides of a bilaterally symmetric trait are the result of the actions of a single genome, fluctuating asymmetry represents an epigenetic measure of the sensitivity of development to stress. Different morphological traits may show a direct relationship between their functional importance and their degree of developmental canalization. This may explain why some characters show high degrees of fluctuating asymmetry, and why these characters more often become exaggerated secondary sexual ornaments. The degree of fluctuating asymmetry is generally larger in small marginal populations living in novel environments, and this will particularly lead to relatively large degrees of asymmetry in the least developmentally canalized traits. More stringent selection against heterozygotes in marginal populations may further break down developmental stability and linkage groups which would lead to increased genetic variance. Females may prefer to mate with males having large, but relatively symmetric morphological characters, because it is more difficult to make large traits (a good genes argument), a large trait is more easily perceived (a sensory bias preference), and because symmetry signals ability to cope with stress (a good genes argument). The low degree of developmental stability and the large amount of genetic variance in secondary sexual characters in small, marginal populations could set the scene for rapid development of divergence and speciation in marginal populations.", 
"Extravagant secondary sexual characters are assumed to have arisen and be maintained by sexual selection. While traits like horns, antlers and spurs can be ascribed to intrasexual competition, other traits such as extravagant feather ornaments, displays and pheromones have to be ascribed to mate choice. A number of studies have tested whether females exert selection on the size of male ornaments, but only some of these have recorded female preferences for the most extravagantly ornamented males. Here I demonstrate that female choice can be directly predicted from the relationship between the degree of fluctuating asymmetry and the size of a secondary sexual character. Fluctuating asymmetry is an epigenetic measure of the ability of individuals to cope with stress, and it occurs when an individual is unable to undergo identical development of an otherwise bilaterally symmetric trait on both sides of its body. There is a negative relationship between the degree of fluctuating asymmetry and the absolute size of an ornament in those bird species with a female preference for the largest male sex trait, while there is a flat or U-shaped relationship among species without a female preference. These results suggest that females prefer exaggerated secondary sexual characters if they reliably demonstrate the ability of males to cope with genetic and environmental stress. Some species may demonstrate a flat or U-shaped relationship between the degree of fluctuating asymmetry and the absolute size of an ornament because (i) the genetic variance in viability signalled by the secondary sex trait has been depleted; (ii) the secondary sex trait is not particularly costly and therefore does not demonstrate condition dependence; or because (iii) the sex traits can be considered arbitrary traits rather than characters reflecting good genes.", 
"Reciprocal embryo transfer experiments show that skeletal dimensions in adult mice are significantly influenced by the genotype of the female providing the uterine environment in which they were raised. Embryo transfers among C3HeB/FeJ, SWR/J, and the C3SWF1 hybrid strain (C3H females x SWR males) permit separation of uterine maternal genotype effects from effects arising from the progeny's own genotype. Many different aspects of adult skeletal form are significantly influenced by uterine genotype and, in some instances, the pattern of these effects correlates with events during skeletal embryology. Analyses involving the highly heterozygous C3SWF1 strain demonstrate the existence of significant dominance in maternal genes affecting skeletal development in the progeny. Further, there is a large skeletal effect due to progeny heterosis. Uterine litter size can be manipulated as a nonheritable component of variability in embryo transfer experiments, and it has a large and systemic effect on skeletal growth and morphogenesis that persists in adult mice. Heritable uterine maternal effects are epigenetic interactions during development that can be incorporated into models of evolutionary change to provide a more complete picture of the causal agents producing morphological change.", 
"Developmental constraint is a theoretically important construct bridging ontogenetic and evolutionary studies. We propose a new operationalization of this notion that exploits the unusually rich measurement structure of landmark data. We represent landmark configurations by their partial warps, a basis for morphospace that represents a set of localized features of form. A finding of developmental constraint arises from the interplay between age-varying means and age-specific variances in these subspaces of morphospace. Examination of variances and means in 16 ventral skull landmarks in the cotton rat S. fulviventer at ages 1, 10, 20, and 30 days yielded three types of developmental constraint: canalization (constraint to relatively constant form age by age); chreods (reduction of variance orthogonal to the mean trajectory over ages); and opposition (reduction of age-specific variance along the mean trajectory over ages). While canalization and chreodic constraints have been noted previously, the oppositional type of constraint appears novel. Only one of our characters, relative length and orientation of the incisive foramen, appears to be canalized. Although skull growth becomes increasingly integrated through ontogeny, our characters display a remarkable spatiotemporal complexity in patterns of variance reduction. The specific assortment of constraints observed may be related to the precociality of Sigmodon. We suggest that Waddington's diagrammatic presentation of the ''epigenetic landscape'' may be misleading in quantitative studies of developmental regulation.", 
"Cladistic analysis of osteological and dental characters in a monophyletic group of Miocene and younger tayassuids demonstrates a pattern of changes in the degree of sexual dimorphism in canine tooth diameter and zygomatic arch width, and in phenotypic correlations between these characters. Primitively, tayassuids have canine teeth that are sexually dimorphic and discretely bimodal in size, and zygomatic arches that are narrow in both sexes. Many late Miocene and Pliocene tayassuids have broad, winglike zygomatic processes. In some species, these processes are large in both sexes, but in others, those of females are much smaller than those of males. The presence of large processes in both sexes is primitive relative to the condition of strong sexual dimorphism. In five separate clades, the zygomatic processes of both sexes become reduced in size, and the degree of sexual dimorphism in canine size becomes reduced as well. The pattern is congruent with predictions derived from a theoretical model of the evolution of sexual dimorphism, and it further indicates the emergence of a new phenotypic correlation between two previously uncorrelated characters, canine size and zygoma size. The advent of this new correlation coincides with the advent of pronounced sexual dimorphism in zygomatic processes. Although such a pattern could be explained by genetically modifying phenotypic expression of homologous characters in one sex or the other, an epigenetic modification of expression is equally plausible: the evolution of sexual dimorphism in homologous characters could be accomplished by placing phenotypic expression of an originally monomorphic character under the control of steroid sex hormones. This hypothesis is consistent with evidence from many vertebrate groups, and it provides testable predictions.", 
" ", 
"We manipulated developmental time and dry weight at eclosion in 15 genotypes of Drosophila melanogaster by growing the larvae in 9 environments defined by 3 yeast concentrations at 3 temperatures. We observed how the genetic and various environmental components of phenotypic variation scaled with the mean values of the traits. Temperature, yeast, within-environmental factors and genotype influenced the genotypic and environmental standard deviations of the two traits in patterns that point to very different modes of physiological and developmental action of these factors. Since different factors affected the environmental and genetic components of the phenotypic variation either in parallel or inversely, we conclude that environmental heterogeneity may have small or large effects on evolutionary rates depending on which factors cause the heterogeneity. The analysis also suggests that the scaling of variances with the mean is not as trivial as is often assumed when coefficients of variation are computed to ''standardize'' variation.",

"The American College of Medical Genetics and Genomics (ACMG) previously developed guidance for the interpretation of sequence variants. 1 In the past decade, sequencing technology has evolved -rapidly with the advent of high-throughput next-generation -sequencing. By adopting and leveraging next-generation sequencing, clinical laboratories are now performing an ever-increasing catalogue of genetic testing spanning genotyping, single genes, gene panels, exomes, genomes, transcriptomes, and epigenetic assays for genetic disorders. By virtue of increased complexity, this shift in genetic testing has been accompanied by new challenges in sequence interpretation. In this context the ACMG convened a workgroup in 2013 comprising representatives from the ACMG, the Association for Molecular Pathology (AMP), and the College of American Pathologists to revisit and revise the standards and guidelines for the interpretation of sequence variants. The group consisted of clinical laboratory directors and clinicians. This report represents expert opinion of the workgroup with input from ACMG, AMP, and College of American Pathologists stakeholders. These recommendations primarily apply to the breadth of genetic tests used in clinical laboratories, including genotyping, single genes, panels, exomes, and genomes. This report recommends the use of specific standard terminology-pathogenic, likely pathogenic, uncertain significance, likely benign, and benign-to describe variants identified in genes that cause Mendelian disorders. Moreover, this recommendation describes a process for classifying variants into these five categories based on criteria using typical types of variant evidence (e.g., population data, computational data, functional data, segregation data). Because of the increased complexity of analysis and interpretation of clinical genetic testing described in this report, the ACMG strongly recommends that clinical molecular genetic testing should be performed in a Clinical Laboratory Improvement Amendments-approved laboratory, with results interpreted by a board-certified clinical molecular geneticist or molecular genetic pathologist or the equivalent.", 
"There is substantial heterogeneity among primary prostate cancers, evident in the spectrum of molecular abnormalities and its variable clinical course. As part of The Cancer Genome Atlas (TCGA), we present a comprehensive molecular analysis of 333 primary prostate carcinomas. Our results revealed a molecular taxonomy in which 74% of these tumors fell into one of seven subtypes defined by specific gene fusions (ERG, ETV1/4, and FLI1) or mutations (SPOP, FOXA1, and IDH1). Epigenetic profiles showed substantial heterogeneity, including an IDH1 mutant subset with a methylator phenotype. Androgen receptor (AR) activity varied widely and in a subtype-specific manner, with SPOP and FOXA1 mutant tumors having the highest levels of AR-induced transcripts. 25% of the prostate cancers had a presumed actionable lesion in the PI3K or MAPK signaling pathways, and DNA repair genes were inactivated in 19%. Our analysis reveals molecular heterogeneity among primary prostate cancers, as well as potentially actionable molecular defects.", 
"PD-L1 and PD-1 (PD) pathway blockade is a highly promising therapy and has elicited durable antitumor responses and long-term remissions in a subset of patients with a broad spectrum of cancers. How to improve, widen, and predict the clinical response to anti-PD therapy is a central theme in the field of cancer immunology and immunotherapy. Oncologic, immunologic, genetic, and biological studies focused on the human cancer microenvironment have yielded substantial insight into this issue. Here, we focus on tumor microenvironment and evaluate several potential therapeutic response markers including the PD-L1 and PD-1 expression pattern, genetic mutations within cancer cells and neoantigens, cancer epigenetics and effector T cell landscape, and microbiota. We further clarify the mechanisms of action of these markers and their roles in shaping, being shaped, and/or predicting therapeutic responses. We also discuss a variety of combinations with PD pathway blockade and their scientific rationales for cancer treatment.", 
"Ensembl (ext-link-type=uri xlink:href=http://www.ensembl.org xlink:type=simple>http://www.ensembl.org) is a genomic interpretation system providing the most up-to-date annotations, querying tools and access methods for chordates and key model organisms. This year we released updated annotation (gene models, comparative genomics, regulatory regions and variation) on the new human assembly, GRCh38, although we continue to support researchers using the GRCh37.p13 assembly through a dedicated site (ext-link-type=uri xlink:href=http://grch37.ensembl.org xlink:type=simple>http://grch37.ensembl.org). Our Regulatory Build has been revamped to identify regulatory regions of interest and to efficiently highlight their activity across disparate epigenetic data sets. A number of new interfaces allow users to perform large-scale comparisons of their data against our annotations. The REST server (ext-link-type=uri xlink:href=http://rest.ensembl.org xlink:type=simple>http://rest.ensembl.org), which allows programs written in any language to query our databases, has moved to a full service alongside our upgraded website tools. Our online Variant Effect Predictor tool has been updated to process more variants and calculate summary statistics. Lastly, the WiggleTools package enables users to summarize large collections of data sets and view them as single tracks in Ensembl. The Ensembl code base itself is more accessible: it is now hosted on our GitHub organization page (ext-link-type=uri xlink:href=https://github.com/Ensembl xlink:type=simple>https://github.com/Ensembl) under an Apache 2.0 open source license.", 
"Over the past 20 years, breakthrough discoveries of chromatin-modifying enzymes and associated mechanisms that alter chromatin in response to physiological or pathological signals have transformed our knowledge of epigenetics from a collection of curious biological phenomena to a functionally dissected research field. Here, we provide a personal perspective on the development of epigenetics, from its historical origins to what we define as 'the modern era of epigenetic research'. We primarily highlight key molecular mechanisms of and conceptual advances in epigenetic control that have changed our understanding of normal and perturbed development.", 
"Single-molecule, real-time sequencing developed by Pacific BioSciences offers longer read lengths than the second-generation sequencing (SGS) technologies, making it well-suited for unsolved problems in genome, transcriptome, and epigenetics research. The highly-contiguous de novo assemblies using PacBio sequencing can close gaps in current reference assemblies and characterize structural variation (SV) in personal genomes. With longer reads, we can sequence through extended repetitive regions and detect mutations, many of which are associated with diseases. Moreover, PacBio transcriptome sequencing is advantageous for the identification of gene isoforms and facilitates reliable discoveries of novel genes and novel isoforms of annotated genes, due to its ability to sequence full-length transcripts or fragments with significant lengths. Additionally, PacBio's sequencing technique provides information that is useful for the direct detection of base modifications, such as methylation. In addition to using PacBio sequencing alone, many hybrid sequencing strategies have been developed to make use of more accurate short reads in conjunction with PacBio long reads. In general, hybrid sequencing strategies are more affordable and scalable especially for small-size laboratories than using PacBio Sequencing alone. The advent of PacBio sequencing has made available much information that could not be obtained via SGS alone.", 
"MicroRNAs (miRNAs) are endogenous, small non-coding RNAs that function in regulation of gene expression. Compelling evidences have demonstrated that miRNA expression is dysregulated in human cancer through various mechanisms, including amplification or deletion of miRNA genes, abnormal transcriptional control of miRNAs, dysregulated epigenetic changes and defects in the miRNA biogenesis machinery. MiRNAs may function as either oncogenes or tumor suppressors under certain conditions. The dysregulated miRNAs have been shown to affect the hallmarks of cancer, including sustaining proliferative signaling, evading growth suppressors, resisting cell death, activating invasion and metastasis, and inducing angiogenesis. An increasing number of studies have identified miRNAs as potential biomarkers for human cancer diagnosis, prognosis and therapeutic targets or tools, which needs further investigation and validation. In this review, we focus on how miRNAs regulate the development of human tumors by acting as tumor suppressors or oncogenes.", 
"'If G-quadruplexes form so readily in vitro, Nature will have found a way of using them in vivo' (Statement by Aaron Klug over 30 years ago). During the last decade, four-stranded helical structures called G-quadruplex (or G4) have emerged from being a structural curiosity observed in vitro, to being recognized as a possible nucleic acid based mechanism for regulating multiple biological processes in vivo. The sequencing of many genomes has revealed that they are rich in sequence motifs that have the potential to form G-quadruplexes and that their location is non-random, correlating with functionally important genomic regions. In this short review, we summarize recent evidence for the in vivo presence and function of DNA and RNA G-quadruplexes in various cellular pathways including DNA replication, gene expression and telomere maintenance. We also highlight remaining open questions that will have to be addressed in the future.", 
"The aberrant expression of transcription factor Basonuclin (BNC) had been reported in different kinds of tumors. Here, we investigated the expression and methylation status of two Basonuclin homologs, BNC1 and BNC2 in hepatocellular carcinoma (HCC). We found that the expression levels of both BNC1 and BNC2 were down-regulated in HCC cell lines and primary HCC tissues. The frequency and intensity of BNC1 promoter hypermethylation in tumor tissues was significantly higher than that in adjacent non-tumor tissues. 5-Aza-2'-Deoxycytidine treatment could significantly increase the BNC1 expression in the methylated HCC cell lines, which implicated that epigenetic modification contributed to the down-regulation of BNC1. In addition, BNC1 hypermethylation in tumor tissues was more likely to happen in female patients. No methylation of the BNC2 promoter was found in HCC tumor tissues. However, a frequent deletion of the BNC2 gene was observed, which indicated that the chromosomal loss of the BNC2 gene might be one important reason for its lower expression level in HCC. Our results suggested that BNC1 and BNC2 were down-regulated in HCC which may provide new insight into the tumorigenesis of HCC.", 
"An increasingly recognized resistance mechanism to androgen receptor (AR)-directed therapy in prostate cancer involves epithelial plasticity, in which tumor cells demonstrate low to absent AR expression and often have neuroendocrine features. The etiology and molecular basis for this 'alternative' treatment-resistant cell state remain incompletely understood. Here, by analyzing whole-exome sequencing data of metastatic biopsies from patients, we observed substantial genomic overlap between castration-resistant tumors that were histologically characterized as prostate adenocarcinomas (CRPC-Adeno) and neuroendocrine prostate cancer (CRPC-NE); analysis of biopsy samples from the same individuals over time points to a model most consistent with divergent clonal evolution. Genome-wide DNA methylation analysis revealed marked epigenetic differences between CRPC-NE tumors and CRPC-Adeno, and also designated samples of CRPC-Adeno with clinical features of AR independence as CRPC-NE, suggesting that epigenetic modifiers may play a role in the induction and/or maintenance of this treatment-resistant state. This study supports the emergence of an alternative, 'AR-indifferent' cell state through divergent clonal evolution as a mechanism of treatment resistance in advanced prostate cancer.", 
"TP53 is the most frequently mutated gene in human cancer. Functionally, p53 is activated by a host of stress stimuli and, in turn, governs an exquisitely complex anti-proliferative transcriptional program that touches upon a bewildering array of biological responses. Despite the many unveiled facets of the p53 network, a clear appreciation of how and in what contexts p53 exerts its diverse effects remains unclear. How can we interpret p53's disparate activities and the consequences of its dysfunction to understand how cell type, mutation profile, and epigenetic cell state dictate outcomes, and how might we restore its tumor-suppressive activities in cancer?", 
"The field of machine learning, which aims to develop computer algorithms that improve with experience, holds promise to enable computers to assist humans in the analysis of large, complex data sets. Here, we provide an overview of machine learning applications for the analysis of genome sequencing data sets, including the annotation of sequence elements and epigenetic, proteomic or metabolomic data. We present considerations and recurrent challenges in the application of supervised, semi-supervised and unsupervised machine learning methods, as well as of generative and discriminative modelling approaches. We provide general guidelines to assist in the selection of these machine learning methods and their practical application for the analysis of genetic and genomic data sets.", 
"Mammalian DNA methylation is a critical epigenetic mechanism orchestrating gene expression networks in many biological processes. However, investigation of the functions of specific methylation events remains challenging. Here, we demonstrate that fusion of Tet1 or Dnmt3a with a catalytically inactive Cas9 (dCas9) enables targeted DNA methylation editing. Targeting of the dCas9-Tet1 or -Dnmt3a fusion protein to methylated or unmethylated promoter sequences caused activation or silencing, respectively, of an endogenous reporter. Targeted demethylation of the BDNF promoter IV or the MyoD distal enhancer by dCas9-Tet1 induced BDNF expression in post-mitotic neurons or activated MyoD facilitating reprogramming of fibroblasts into myoblasts, respectively. Targeted de novo methylation of a CTCF loop anchor site by dCas9-Dnmt3a blocked CTCF binding and interfered with DNA looping, causing altered gene expression in the neighboring loop. Finally, we show that these tools can edit DNA methylation in mice, demonstrating their wide utility for functional studies of epigenetic regulation.", 
"Diverse classes of RNA, ranging from small to long non-coding RNAs, have emerged as key regulators of gene expression, genome stability and defence against foreign genetic elements. Small RNAs modify chromatin structure and silence transcription by guiding Argonaute-containing complexes to complementary nascent RNA scaffolds and then mediating the recruitment of histone and DNA methyltransferases. In addition, recent advances suggest that chromatin-associated long non-coding RNA scaffolds also recruit chromatin-modifying complexes independently of small RNAs. These co-transcriptional silencing mechanisms form powerful RNA surveillance systems that detect and silence inappropriate transcription events, and provide a memory of these events via self-reinforcing epigenetic loops.", 
"Next-generation sequencing has revealed that more than 50% of human cancers harbour mutations in enzymes that are involved in chromatin organization. Tumour cells not only are activated by genetic and epigenetic alterations, but also routinely use epigenetic processes to ensure their escape from chemotherapy and host immune surveillance. Hence, a growing emphasis of recent drug discovery efforts has been on targeting the epigenome, including DNA methylation and histone modifications, with several new drugs being tested and some already approved by the US Food and Drug Administration (FDA). The future will see the increasing success of combining epigenetic drugs with other therapies. As epigenetic drugs target the epigenome as a whole, these true 'genomic medicines' lessen the need for precision approaches to individualized therapies.", 
"One-carbon (1C) metabolism, mediated by the folate cofactor, supports multiple physiological processes. These include biosynthesis (purines and thymidine), amino acid homeostasis (glycine, serine, and methionine), epigenetic maintenance, and redox defense. Both within eukaryotic cells and across organs, 1C metabolic reactions are compartmentalized. Here we review the fundamentals of mammalian 1C metabolism, including the pathways active in different compartments, cell types, and biological states. Emphasis is given to recent discoveries enabled by modern genetics, analytical chemistry, and isotope tracing. An emerging theme is the biological importance of mitochondrial 1C reactions, both for producing 1C units that are exported to the cytosol and for making additional products, including glycine and NADPH. Increased clarity regarding differential folate pathway usage in cancer, stem cells, development, and adult physiology is reviewed and highlights new opportunities for selective therapeutic intervention.", 
"Acetyl-coenzyme A (acetyl-CoA) is a central metabolic intermediate. The abundance of acetyl-CoA in distinct subcellular compartments reflects the general energetic state of the cell. Moreover, acetyl-CoA concentrations influence the activity or specificity of multiple enzymes, either in an allosteric manner or by altering substrate availability. Finally, by influencing the acetylation profile of several proteins, including histones, acetyl-CoA controls key cellular processes, including energy metabolism, mitosis, and autophagy, both directly and via the epigenetic regulation of gene expression. Thus, acetyl-CoA determines the balance between cellular catabolism and anabolism by simultaneously operating as a metabolic intermediate and as a second messenger.", 
"Cancer growth and progression are associated with immune suppression. Cancer cells have the ability to activate different immune checkpoint pathways that harbor immunosuppressive functions. Monoclonal antibodies that target immune checkpoints provided an immense breakthrough in cancer therapeutics. Among the immune checkpoint inhibitors, PD-1/PD-L1 and CTLA-4 inhibitors showed promising therapeutic outcomes, and some have been approved for certain cancer treatments, while others are under clinical trials. Recent reports have shown that patients with various malignancies benefit from immune checkpoint inhibitor treatment. However, mainstream initiation of immune checkpoint therapy to treat cancers is obstructed by the low response rate and immune-related adverse events in some cancer patients. This has given rise to the need for developing sets of biomarkers that predict the response to immune checkpoint blockade and immune-related adverse events. In this review, we discuss different predictive biomarkers for anti-PD-1/PD-L1 and anti-CTLA-4 inhibitors, including immune cells, PD-L1 overexpression, neoantigens, and genetic and epigenetic signatures. Potential approaches for further developing highly reliable predictive biomarkers should facilitate patient selection for and decision-making related to immune checkpoint inhibitor-based therapies.", 
"Nucleosome positioning varies between cell types. By deep sequencing cell-free DNA (cfDNA), isolated from circulating blood plasma, we generated maps of genome-wide in vivo nucleosome occupancy and found that short cfDNA fragments harbor footprints of transcription factors. The cfDNA nucleosome occupancies correlate well with the nuclear architecture, gene structure, and expression observed in cells, suggesting that they could inform the cell type of origin. Nucleosome spacing inferred from cfDNA in healthy individuals correlates most strongly with epigenetic features of lymphoid and myeloid cells, consistent with hematopoietic cell death as the normal source of cfDNA. We build on this observation to show how nucleosome footprints can be used to infer cell types contributing to cfDNA in pathological states such as cancer. Since this strategy does not rely on genetic differences to distinguish between contributing tissues, it may enable the noninvasive monitoring of a much broader set of clinical conditions than currently possible.", 
"The Cas9 protein (CRISPR-associated protein 9), derived from type II CRISPR (clustered regularly interspaced short palindromic repeats) bacterial immune systems, is emerging as a powerful tool for engineering the genome in diverse organisms. As an RNA-guided DNA endonuclease, Cas9 can be easily programmed to target new sites by altering its guide RNA sequence, and its development as a tool has made sequence-specific gene editing several magnitudes easier. The nuclease-deactivated form of Cas9 further provides a versatile RNA-guided DNA-targeting platform for regulating and imaging the genome, as well as for rewriting the epigenetic status, all in a sequence-specific manner. With all of these advances, we have just begun to explore the possible applications of Cas9 in biomedical research and therapeutics. In this review, we describe the current models of Cas9 function and the structural and biochemical studies that support it. We focus on the applications of Cas9 for genome editing, regulation, and imaging, discuss other possible applications and some technical considerations, and highlight the many advantages that CRISPR/Cas9 technology offers.", 
"Carcinogenesis cannot be explained only by genetic alterations, but also involves epigenetic processes. Modification of histones by acetylation plays a key role in epigenetic regulation of gene expression and is controlled by the balance between histone deacetylases (HDAC) and histone acetyltransferases (HAT). HDAC inhibitors induce cancer cell cycle arrest, differentiation and cell death, reduce angiogenesis and modulate immune response. Mechanisms of anticancer effects of HDAC inhibitors are not uniform; they may be different and depend on the cancer type, HDAC inhibitors, doses, etc. HDAC inhibitors seem to be promising anti-cancer drugs particularly in the combination with other anti-cancer drugs and/or radiotherapy. HDAC inhibitors vorinostat, romidepsin and belinostat have been approved for some T-cell lymphoma and panobinostat for multiple myeloma. Other HDAC inhibitors are in clinical trials for the treatment of hematological and solid malignancies. The results of such studies are promising but further larger studies are needed. Because of the reversibility of epigenetic changes during cancer development, the potency of epigenetic therapies seems to be of great importance. Here, we summarize the data on different classes of HDAC inhibitors, mechanisms of their actions and discuss novel results of preclinical and clinical studies, including the combination with other therapeutic modalities.", 
"The finding that small non-coding RNAs (ncRNAs) are able to control gene expression in a sequence specific manner has had a massive impact on biology. Recent improvements in high throughput sequencing and computational prediction methods have allowed the discovery and classification of several types of ncRNAs. Based on their precursor structures, biogenesis pathways and modes of action, ncRNAs are classified as small interfering RNAs (siRNAs), microRNAs (miRNAs), PIWI-interacting RNAs (piRNAs), endogenous small interfering RNAs (endo-siRNAs or esiRNAs), promoter associate RNAs (pRNAs), small nucleolar RNAs (snoRNAs) and sno-derived RNAs. Among these, miRNAs appear as important cytoplasmic regulators of gene expression. miRNAs act as post-transcriptional regulators of their messenger RNA (mRNA) targets via mRNA degradation and/or translational repression. However, it is becoming evident that miRNAs also have specific nuclear functions. Among these, the most studied and debated activity is the miRNA-guided transcriptional control of gene expression. Although available data detail quite precisely the effectors of this activity, the mechanisms by which miRNAs identify their gene targets to control transcription are still a matter of debate. Here, we focus on nuclear functions of miRNAs and on alternative mechanisms of target recognition, at the promoter lavel, by miRNAs in carrying out transcriptional gene silencing.", 
"Since decades it has been known that non-protein-coding RNAs have important cellular functions. Deep sequencing recently facilitated the discovery of thousands of novel transcripts, now classified as long noncoding RNAs (lncRNAs), in many vertebrate and invertebrate species. LncRNAs are involved in a wide range of cellular mechanisms, from almost all aspects of gene expression to protein translation and stability. Recent findings implicate lncRNAs as key players of cellular differentiation, cell lineage choice, organogenesis and tissue homeostasis. Moreover, lncRNAs are involved in pathological conditions such as cancer and cardiovascular disease, and therefore provide novel biomarkers and pharmaceutical targets. Here we discuss examples illustrating the versatility of lncRNAs in gene control, development and differentiation, as well as in human disease.", 
"Identifying and validating molecular targets of interventions that extend the human health span and lifespan has been difficult, as most clinical biomarkers are not sufficiently representative of the fundamental mechanisms of ageing to serve as their indicators. In a recent breakthrough, biomarkers of ageing based on DNA methylation data have enabled accurate age estimates for any tissue across the entire life course. These 'epigenetic clocks' link developmental and maintenance processes to biological ageing, giving rise to a unified theory of life course. Epigenetic biomarkers may help to address long-standing questions in many fields, including the central question: why do we age?", 
"Epithelial-mesenchymal transition (EMT) is a process in which epithelial cells acquire mesenchymal features. In cancer, EMT is associated with tumor initiation, invasion, metastasis, and resistance to therapy. Recently, it has been demonstrated that EMT is not a binary process, but occurs through distinct cellular states. Here, we review the recent studies that demonstrate the existence of these different EMT states in cancer and the mechanisms regulating their functions. We discuss the different functional characteristics, such as proliferation, propagation, plasticity, invasion, and metastasis associated with the distinct EMT states. We summarize the role of the transcriptional and epigenetic landscapes, gene regulatory network and their surrounding niche in controlling the transition through the different EMT states.", 
"Methylation of DNA and of histone 3 at Lys 9 (H3K9) are highly correlated with gene silencing in eukaryotes from fungi to humans. Both of these epigenetic marks need to be established at specific regions of the genome and then maintained at these sites through cell division. Protein structural domains that specifically recognize methylated DNA and methylated histones are key for targeting enzymes that catalyse these marks to appropriate genome sites. Genetic, genomic, structural and biochemical data reveal connections between these two epigenetic marks, and these domains mediate much of the crosstalk.", 
"This year is the tenth anniversary of the publication in this journal of a model suggesting the existence of 'tumour progenitor genes'. These genes are epigenetically disrupted at the earliest stages of malignancies, even before mutations, and thus cause altered differentiation throughout tumour evolution. The past decade of discovery in cancer epigenetics has revealed a number of similarities between cancer genes and stem cell reprogramming genes, widespread mutations in epigenetic regulators, and the part played by chromatin structure in cellular plasticity in both development and cancer. In the light of these discoveries, we suggest here a framework for cancer epigenetics involving three types of genes: 'epigenetic mediators', corresponding to the tumour progenitor genes suggested earlier; 'epigenetic modifiers' of the mediators, which are frequently mutated in cancer; and 'epigenetic modulators' upstream of the modifiers, which are responsive to changes in the cellular environment and often linked to the nuclear architecture. We suggest that this classification is helpful in framing new diagnostic and therapeutic approaches to cancer.", 
"Specification of primordial germ cells (PGCs) marks the beginning of the totipotent state. However, without a tractable experimental model, the mechanism of human PGC (hPGC) specification remains unclear. Here, we demonstrate specification of hPGC-like cells (hPGCLCs) from germline competent pluripotent stem cells. The characteristics of hPGCLCs are consistent with the embryonic hPGCs and a germline seminoma that share a CD38 cell-surface marker, which collectively defines likely progression of the early human germline. Remarkably, SOX17 is the key regulator of hPGC-like fate, whereas BLIMP1 represses endodermal and other somatic genes during specification of hPGCLCs. Notable mechanistic differences between mouse and human PGC specification could be attributed to their divergent embryonic development and pluripotent states, which might affect other early cell-fate decisions. We have established a foundation for future studies on resetting of the epigenome in hPGCLCs and hPGCs for totipotency and the transmission of genetic and epigenetic information.", 
"The discovery of long non-coding RNA (lncRNA) has dramatically altered our understanding of cancer. Here, we describe a comprehensive analysis of lncRNA alterations at transcriptional, genomic, and epigenetic levels in 5,037 human tumor specimens across 13 cancer types from The Cancer Genome Atlas. Our results suggest that the expression and dysregulation of lncRNAs are highly cancer type specific compared with protein- coding genes. Using the integrative data generated by this analysis, we present a clinically guided small interfering RNA screening strategy and a co-expression analysis approach to identify cancer driver lncRNAs and predict their functions. This provides a resource for investigating lncRNAs in cancer and lays the groundwork for the development of new diagnostics and treatments.", 
"Plant genonnes encode various small RNAs that function in distinct, yet overlapping, genetic and epigenetic silencing pathways. However, the abundance and diversity of small-RNA classes varies among plant species, suggesting coevolution between environmental adaptations and gene-silencing mechanisms. Biogenesis of small RNAs in plants is well understood, but we are just beginning to uncover their intricate regulation and activity. Here, we discuss the biogenesis of plant small RNAs, such as nnicroRNAs, secondary siRNAs and heterochromatic siRNAs, and their diverse cellular and developmental functions, including in reproductive transitions, genomic imprinting and paramutation. We also discuss the diversification of small-RNA-directed silencing pathways through the expansion of RNA-dependent RNA polymerases, DICER proteins and ARGONAUTE proteins.", 
"Epigenetic modifications, including DNA methylation, represent a potential mechanism for environmental impacts on human disease. Maternal smoking in pregnancy remains an important public health problem that impacts child health in a myriad of ways and has potential lifelong consequences. The mechanisms are largely unknown, but epigenetics most likely plays a role. We formed the Pregnancy And Childhood Epigenetics (PACE) consortium and meta-analyzed, across 13 cohorts (n = 6,685), the association between maternal smoking in pregnancy and newborn blood DNA methylation at over 450,000 CpG sites (CpGs) by using the Illumina 450K BeadChip. Over 6,000 CpGs were differentially methylated in relation to maternal smoking at genome-wide statistical significance (false discovery rate, 5%), including 2,965 CpGs corresponding to 2,017 genes not previously related to smoking and methylation in either newborns or adults. Several genes are relevant to diseases that can be caused by maternal smoking (e.g., orofacial clefts and asthma) or adult smoking (e.g., certain cancers). A number of differentially methylated CpGs were associated with gene expression. We observed enrichment in pathways and processes critical to development. In older children (5 cohorts, n = 3,187), 100% of CpGs gave at least nominal levels of significance, far more than expected by chance (p value < 2.2 x 10(-16)). Results were robust to different normalization methods used across studies and cell type adjustment. In this large scale meta-analysis of methylation data, we identified numerous loci involved in response to maternal smoking in pregnancy with persistence into later childhood and provide insights into mechanisms underlying effects of this important exposure.", 
"In 1964, Vincent Allfrey and colleagues reported the identification of histone acetylation and with deep insight proposed a regulatory role for this protein modification in transcription regulation. Subsequently, histone acetyltransferases (HATs), histone deacetylases (HDACs) and acetyl-Lys-binding proteins were identified as transcription regulators, thereby providing compelling evidence for his daring hypothesis. During the past 15 years, reversible protein acetylation and its modifying enzymes have been implicated in many cellular functions beyond transcription regulation. Here, we review the progress accomplished during the past 50 years and discuss the future of protein acetylation.", 
"N-6-methyladenosine (m(6)A) is the most prevalent and internal modification that occurs in the messenger RNAs (mRNA) of most eukaryotes, although its functional relevance remained a mystery for decades. This modification is installed by the m(6)A methylation writers and can be reversed by demethylases that serve as erasers. In this review, we mainly summarize recent progress in the study of the m(6)A mRNA methylation machineries across eukaryotes and discuss their newly uncovered biological functions. The broad roles of m(6)A in regulating cell fates and embryonic development highlight the existence of another layer of epigenetic regulation at the RNA level, where mRNA is subjected to chemical modifications that affect protein expression.", 
"The Bromo- and Extra-Terminal (BET) proteins BRD2, BRD3, and BRD4 play important roles in transcriptional regulation, epigenetics, and cancer and are the targets of pan-BET selective bromodomain inhibitor JQ1. However, the lack of intra-BET selectivity limits the scope of current inhibitors as probes for target validation and could lead to unwanted side effects or toxicity in a therapeutic setting. We designed Proteolysis Targeted Chimeras (PROTACs) that tether JQ1 to a ligand for the E3 ubiquitin ligase VHL, aimed at triggering the intracellular destruction of BET proteins. Compound MZ1 potently and rapidly induces reversible, long-lasting, and unexpectedly selective removal of BRD4 over BRD2 and BRD3. The activity of MZ1 is dependent on binding to VHL but is achieved at a sufficiently low concentration not to induce stabilization of HIF-1 alpha. Gene expression profiles of selected cancer-related genes responsive to JQ1 reveal distinct and more limited transcriptional responses induced by MZ1, consistent with selective suppression of BRD4. Our discovery opens up new opportunities to elucidate the cellular phenotypes and therapeutic implications associated with selective targeting of BRD4.", 
"We define the chromatin accessibility and transcriptional landscapes in 13 human primary blood cell types that span the hematopoietic hierarchy. Exploiting the finding that the enhancer landscape better reflects cell identity than mRNA levels, we enable 'enhancer cytometry' for enumeration of pure cell types from complex populations. We identify regulators governing hematopoietic differentiation and further show the lineage ontogeny of genetic elements linked to diverse human diseases. In acute myeloid leukemia (AML), chromatin accessibility uncovers unique regulatory evolution in cancer cells with a progressively increasing mutation burden. Single AML cells exhibit distinctive mixed regulome profiles corresponding to disparate developmental stages. A method to account for this regulatory heterogeneity identified cancer-specific deviations and implicated HOX factors as key regulators of preleukemic hematopoietic stem cell characteristics. Thus, regulome dynamics can provide diverse insights into hematopoietic development and disease.", 
"Treatment of cancer has been revolutionized by immune checkpoint blockade therapies. Despite the high rate of response in advanced melanoma, the majority of patients succumb to disease. To identify factors associated with success or failure of checkpoint therapy, we profiled transcriptomes of 16,291 individual immune cells from 48 tumor samples of melanoma patients treated with checkpoint inhibitors. Two distinct states of CD8(+) T cells were defined by clustering and associated with patient tumor regression or progression. A single transcription factor, TCF7, was visualized within CD8(+) T cells in fixed tumor samples and predicted positive clinical outcome in an independent cohort of checkpoint-treated patients. We delineated the epigenetic landscape and clonality of these T cell states and demonstrated enhanced antitumor immunity by targeting novel combinations of factors in exhausted cells. Our study of immune cell transcriptomes from tumors demonstrates a strategy for identifying predictors, mechanisms, and targets for enhancing checkpoint immunotherapy.", 
"The extent of tumor heterogeneity is an emerging theme that researchers are only beginning to understand. How genetic and epigenetic heterogeneity affects tumor evolution and clinical progression is unknown. The precise nature of the environmental factors that influence this heterogeneity is also yet to be characterized. Nature Medicine, Nature Biotechnology and the Volkswagen Foundation organized a meeting focused on identifying the obstacles that need to be overcome to advance translational research in and tumor heterogeneity. Once these key questions were established, the attendees devised potential solutions. Their ideas are presented here.", 
"Single-stranded guanine-rich DNA sequences can fold into four-stranded DNA structures called G-quadruplexes (G4s) that arise from the self-stacking of two or more guanine quartets. There has been considerable recent progress in the detection and mapping of G4 structures in the human genome and in biologically relevant contexts. These advancements, many of which align with predictions made previously in computational studies, provide important new insights into the functions of G4 structures in, for example, the regulation of transcription and genome stability, and uncover their potential relevance for cancer therapy.", 
"Humans show strong sex differences in immunity to infection and autoimmunity, suggesting sex hormones modulate immune responses. Indeed, receptors for estrogens (ERs) regulate cells and pathways in the innate and adaptive immune system, as well as immune cell development. ERs are ligand-dependent transcription factors that mediate long-range chromatin interactions and form complexes at gene regulatory elements, thus promoting epigenetic changes and transcription. ERs also participate in membrane-initiated steroid signaling to generate rapid responses. Estradiol and ER activity show profound dose- and context-dependent effects on innate immune signaling pathways and myeloid cell development. While estradiol most often promotes the production of type I interferon, innate pathways leading to pro-inflammatory cytokine production may be enhanced or dampened by ER activity. Regulation of innate immune cells and signaling by ERs may contribute to the reported sex differences in innate immune pathways. Here we review the recent literature and highlight several molecular mechanisms by which ERs regulate the development or functional responses of innate immune cells. (C) 2015 Elsevier Inc. All rights reserved.", 
"Epigenetic studies relied so far on correlations between epigenetic marks and gene expression pattern. Technologies developed for epigenome editing now enable direct study of functional relevance of precise epigenetic modifications and gene regulation. The reversible nature of epigenetic modifications, including DNA methylation, has been already exploited in cancer therapy for remodeling the aberrant epigenetic landscape. However, this was achieved non-selectively using epigenetic inhibitors. Epigenetic editing at specific loci represents a novel approach that might selectively and heritably alter gene expression. Here, we developed a CRISPR-Cas9-based tool for specific DNA methylation consisting of deactivated Cas9 (dCas9) nuclease and catalytic domain of the DNA methyltransferase DNMT3A targeted by co-expression of a guide RNA to any 20 bp DNA sequence followed by the NGG trinucleotide. We demonstrated targeted CpG methylation in a similar to 35 bp wide region by the fusion protein. We also showed that multiple guide RNAs could target the dCas9-DNMT3A construct to multiple adjacent sites, which enabled methylation of a larger part of the promoter. DNA methylation activity was specific for the targeted region and heritable across mitotic divisions. Finally, we demonstrated that directed DNA methylation of a wider promoter region of the target loci IL6ST and BACH2 decreased their expression.", 
"The DNA methyltransferase (DNMT) family comprises a conserved set of DNA-modifying enzymes that have a central role in epigenetic gene regulation. Recent studies have shown that the functions of the canonical DNMT enzymes-DNMT1, DNMT3A and DNMT3B-go beyond their traditional roles of establishing and maintaining DNA methylation patterns. This Review analyses how molecular interactions and changes in gene copy numbers modulate the activity of DNMTs in diverse gene regulatory functions, including transcriptional silencing, transcriptional activation and post-transcriptional regulation by DNMT2-dependent tRNA methylation. This mechanistic diversity enables the DNMT family to function as a versatile toolkit for epigenetic regulation.", 
"Estimates of biological age based on DNA methylation patterns, often referred to as epigenetic age, DNAm age, have been shown to be robust biomarkers of age in humans. We previously demonstrated that independent of chronological age, epigenetic age assessed in blood predicted all-cause mortality in four human cohorts. Here, we expanded our original observation to 13 different cohorts for a total sample size of 13,089 individuals, including three racial/ethnic groups. In addition, we examined whether incorporating information on blood cell composition into the epigenetic age metrics improves their predictive power for mortality. All considered measures of epigenetic age acceleration were predictive of mortality (p <= 8.2x10(-9)), independent of chronological age, even after adjusting for additional risk factors (p<5.4x10(-4)), and within the racial/ethnic groups that we examined (non-Hispanic whites, Hispanics, African Americans). Epigenetic age estimates that incorporated information on blood cell composition led to the smallest p-values for time to death (p=7.5x10(-43)). Overall, this study a) strengthens the evidence that epigenetic age predicts all-cause mortality above and beyond chronological age and traditional risk factors, and b) demonstrates that epigenetic age estimates that incorporate information on blood cell counts lead to highly significant associations with all-cause mortality.", 
"Childhood trauma confers higher risk of adulthood physical and mental illness; however, the biological mechanism mediating this association remains largely unknown. Recent research has suggested dysregulation of the immune system as a possible biological mediator. The present paper conducted a meta-analysis to establish whether early-life adversity contributes to potentially pathogenic pro-inflammatory phenotypes in adult individuals. A systematic search of Pubmed, PsycINFO, EMBASE, Scopus and Medline identified 25 articles for the meta-analysis, including 18 studies encompassing a sample of 16 870 individuals for C-reactive protein (CRP), 15 studies including 3751 individuals for interleukin-6 (IL-6) and 10 studies including 881 individuals for tumour necrosis factor-alpha (TNF-alpha). Random-effects meta-analysis showed that individuals exposed to childhood trauma had significantly elevated baseline peripheral levels of CRP (Fisher's z = 0.10, 95% confidence interval (CI) = 0.05-0.14), IL-6 (z = 0.08, 95% CI = 0.03-0.14) and TNF-alpha (z = 0.23, 95% CI = 0.14-0.32). Subgroup analyses for specific types of trauma (sexual, physical or emotional abuse) revealed that these impact differentially the single inflammatory markers. Moreover, meta-regression revealed greater effect sizes in clinical samples for the association between childhood trauma and CRP but not for IL-6 or TNF-alpha. Age, body mass index (BMI) and gender had no moderating effects. The analysis demonstrates that childhood trauma contributes to a pro-inflammatory state in adulthood, with specific inflammatory profiles depending on the specific type of trauma.", 
"The heart must continuously pump blood to supply the body with oxygen and nutrients. To maintain the high energy consumption required by this role, the heart is equipped with multiple complex biological systems that allow adaptation to changes of systemic demand. The processes of growth (hypertrophy), angiogenesis, and metabolic plasticity are critically involved in maintenance of cardiac homeostasis. Cardiac hypertrophy is classified as physiological when it is associated with normal cardiac function or as pathological when associated with cardiac dysfunction. Physiological hypertrophy of the heart occurs in response to normal growth of children or during pregnancy, as well as in athletes. In contrast, pathological hypertrophy is induced by factors such as prolonged and abnormal hemodynamic stress, due to hypertension, myocardial infarction etc. Pathological hypertrophy is associated with fibrosis, capillary rarefaction, increased production of pro-inflammatory cytokines, and cellular dysfunction (impairment of signaling, suppression of autophagy, and abnormal cardiomyocyte/non-cardiomyocyte interactions), as well as undesirable epigenetic changes, with these complex responses leading to maladaptive cardiac remodeling and heart failure. This review describes the key molecules and cellular responses involved in physiological/pathological cardiac hypertrophy. (C) 2016 Elsevier Ltd. All rights reserved.", 
"The process of aging results in a host of changes at the cellular and molecular levels, which include senescence, telomere shortening, and changes in gene expression. Epigenetic patterns also change over the lifespan, suggesting that epigenetic changes may constitute an important component of the aging process. The epigenetic mark that has been most highly studied is DNA methylation, the presence of methyl groups at CpG dinucleotides. These dinucleotides are often located near gene promoters and associate with gene expression levels. Early studies indicated that global levels of DNA methylation increase over the first few years of life and then decrease beginning in late adulthood. Recently, with the advent of microarray and next-generation sequencing technologies, increases in variability of DNA methylation with age have been observed, and a number of site-specific patterns have been identified. It has also been shown that certain CpG sites are highly associated with age, to the extent that prediction models using a small number of these sites can accurately predict the chronological age of the donor. Together, these observations point to the existence of two phenomena that both contribute to age-related DNA methylation changes: epigenetic drift and the epigenetic clock. In this review, we focus on healthy human aging throughout the lifetime and discuss the dynamics of DNA methylation as well as how interactions between the genome, environment, and the epigenome influence aging rates. We also discuss the impact of determining 'epigenetic age' for human health and outline some important caveats to existing and future studies.", 
"The ability to rapidly restore the integrity of a broken skin barrier is critical and is the ultimate goal of therapies for hard-to-heal-ulcers. Unfortunately effective treatments to enhance healing and reduce scarring are still lacking. A deeper understanding of the physiology of normal repair and of the pathology of delayed healing is a prerequisite for the development of more effective therapeutic interventions. Transition from the inflammatory to the proliferative phase is a key step during healing and accumulating evidence associates a compromised transition with wound healing disorders. Thus, targeting factors that impact this phase transition may offer a rationale for therapeutic development. This review summarizes mechanisms regulating the inflammation-proliferation transition at cellular and molecular levels. We propose that identification of such mechanisms will reveal promising targets for development of more effective therapies.", 
"Adult somatic stem cells in various organs maintain homeostatic tissue regeneration and enhance plasticity. Since its initial discovery five decades ago, investigations of adult neurogenesis and neural stem cells have led to an established and expanding field that has significantly influenced many facets of neuroscience, developmental biology, and regenerative medicine. Here we review recent progress and focus on questions related to adult mammalian neural stem cells that also apply to other somatic stem cells. We further discuss emerging topics that are guiding the field toward better understanding adult neural stem cells and ultimately applying these principles to improve human health.", 
"The dogma that adaptive immunity is the only arm of the immune response with memory capacity has been recently challenged by several studies demonstrating evidence for memory-like innate immune training. However, the underlying mechanisms and location for generating such innate memory responses in vivo remain unknown. Here, we show that access of Bacillus Calmette-Guerin (BCG) to the bone marrow (BM) changes the transcriptional landscape of hematopoietic stem cells (HSCs) and multipotent progenitors (MPPs), leading to local cell expansion and enhanced myelopoiesis at the expense of lymphopoiesis. Importantly, BCG-educated HSCs generate epigenetically modified macrophages that provide significantly better protection against virulent M. tuberculosis infection than naive macrophages. By using parabiotic and chimeric mice, as well as adoptive transfer approaches, we demonstrate that training of the monocyte/macrophage lineage via BCG-induced HSC reprogramming is sustainable in vivo. Our results indicate that targeting the HSC compartment provides a novel approach for vaccine development.", 
"Experimental modelling of human disorders enables the definition of the cellular and molecular mechanisms underlying diseases and the development of therapies for treating them. The availability of human pluripotent stem cells (PSCs), which are capable of self-renewal and have the potential to differentiate into virtually any cell type, can now help to overcome the limitations of animal models for certain disorders. The ability to model human diseases using cultured PSCs has revolutionized the ways in which we study monogenic, complex and epigenetic disorders, as well as early- and late-onset diseases. Several strategies are used to generate such disease models using either embryonic stem cells (ES cells) or patient-specific induced PSCs (iPSCs), creating new possibilities for the establishment of models and their use in drug screening.", 
"Resetting of the epigenome in human primordial germ cells (hPGCs) is critical for development. We show that the transcriptional program of hPGCs is distinct from that in mice, with co-expression of somatic specifiers and naive pluripotency genes TFCP2L1 and KLF4. This unique gene regulatory network, established by SOX17 and BLIMP1, drives comprehensive germline DNA demethylation by repressing DNA methylation pathways and activating TET-mediated hydroxymethylation. Base-resolution methylome analysis reveals progressive DNA demethylation to basal levels in week 5-7 in vivo hPGCs. Concurrently, hPGCs undergo chromatin reorganization, X reactivation, and imprint erasure. Despite global hypomethylation, evolutionarily young and potentially hazardous retroelements, like SVA, remain methylated. Remarkably, some loci associated with metabolic and neurological disorders are also resistant to DNA demethylation, revealing potential for transgenerational epigenetic inheritance that may have phenotypic consequences. We provide comprehensive insight on early human germline transcriptional network and epigenetic reprogramming that subsequently impacts human development and disease.", 
"The cBioPortal for Cancer Genomics (http://cbioportal.org) provides a Web resource for exploring, visualizing, and analyzing multidimensional cancer genomics data. The portal reduces molecular profiling data from cancer tissues and cell lines into readily understandable genetic, epigenetic, gene expression, and proteomic events. The query interface combined with customized data storage enables researchers to interactively explore genetic alterations across samples, genes, and pathways and, when available in the underlying data, to link these to clinical outcomes. The portal provides graphical summaries of gene-level data from multiple platforms, network visualization and analysis, survival analysis, patient-centric queries, and software programmatic access. The intuitive Web interface of the portal makes complex cancer genomics profiles accessible to researchers and clinicians without requiring bioinformatics expertise, thus facilitating biological discoveries. Here, we provide a practical guide to the analysis and visualization features of the cBioPortal for Cancer Genomics.", 
"Aging is characterized by a progressive loss of physiological integrity, leading to impaired function and increased vulnerability to death. This deterioration is the primary risk factor for major human pathologies, including cancer, diabetes, cardiovascular disorders, and neurodegenerative diseases. Aging research has experienced an unprecedented advance over recent years, particularly with the discovery that the rate of aging is controlled, at least to some extent, by genetic pathways and biochemical processes conserved in evolution. This Review enumerates nine tentative hallmarks that represent common denominators of aging in different organisms, with special emphasis on mammalian aging. These hallmarks are: genomic instability, telomere attrition, epigenetic alterations, loss of proteostasis, deregulated nutrient sensing, mitochondrial dysfunction, cellular senescence, stem cell exhaustion, and altered intercellular communication. A major challenge is to dissect the interconnectedness between the candidate hallmarks and their relative contributions to aging, with the final goal of identifying pharmaceutical targets to improve human health during aging, with minimal side effects.", 
"DNA methylation is frequently described as a 'silencing' epigenetic mark, and indeed this function of 5-methylcytosine was originally proposed in the 1970s. Now, thanks to improved genome-scale mapping of methylation, we can evaluate DNA methylation in different genomic contexts: transcriptional start sites with or without CpG islands, in gene bodies, at regulatory elements and at repeat sequences. The emerging picture is that the function of DNA methylation seems to vary with context, and the relationship between DNA methylation and transcription is more nuanced than we realized at first. Improving our understanding of the functions of DNA methylation is necessary for interpreting changes in this mark that are observed in diseases such as cancer.", 
"The Cancer Genome Atlas (TCGA) Research Network has profiled and analyzed large numbers of human tumors to discover molecular aberrations at the DNA, RNA, protein and epigenetic levels. The resulting rich data provide a major opportunity to develop an integrated picture of commonalities, differences and emergent themes across tumor lineages. The Pan-Cancer initiative compares the first 12 tumor types profiled by TCGA. Analysis of the molecular aberrations and their functional roles across tumor types will teach us how to extend therapies effective in one cancer type to others with a similar genomic profile.", 
"The central dogma of gene expression is that DNA is transcribed into messenger RNAs, which in turn serve as the template for protein synthesis. The discovery of extensive transcription of large RNA transcripts that do not code for proteins, termed long noncoding RNAs (lncRNAs), provides an important new perspective on the centrality of RNA in gene regulation. Here, we discuss genome-scale strategies to discover and characterize lncRNAs. An emerging theme from multiple model systems is that lncRNAs form extensive networks of ribonucleoprotein (RNP) complexes with numerous chromatin regulators and then target these enzymatic activities to appropriate locations in the genome. Consistent with this notion, lncRNAs can function as modular scaffolds to specify higher-order organization in RNP complexes and in chromatin states. The importance of these modes of regulation is underscored by the newly recognized roles of long RNAs for proper gene control across all kingdoms of life.", 
"Metastases represent the end products of a multistep cell-biological process termed the invasion-metastasis cascade, which involves dissemination of cancer cells to anatomically distant organ sites and their subsequent adaptation to foreign tissue microenvironments. Each of these events is driven by the acquisition of genetic and/or epigenetic alterations within tumor cells and the co-option of nonneoplastic stromal cells, which together endow incipient metastatic cells with traits needed to generate macroscopic metastases. Recent advances provide provocative insights into these cell-biological and molecular changes, which have implications regarding the steps of the invasion-metastasis cascade that appear amenable to therapeutic targeting.", 
"Background: It is not yet known whether DNA methylation levels can be used to accurately predict age across a broad spectrum of human tissues and cell types, nor whether the resulting age prediction is a biologically meaningful measure. Results: I developed a multi-tissue predictor of age that allows one to estimate the DNA methylation age of most tissues and cell types. The predictor, which is freely available, was developed using 8,000 samples from 82 Illumina DNA methylation array datasets, encompassing 51 healthy tissues and cell types. I found that DNA methylation age has the following properties: first, it is close to zero for embryonic and induced pluripotent stem cells; second, it correlates with cell passage number; third, it gives rise to a highly heritable measure of age acceleration; and, fourth, it is applicable to chimpanzee tissues. Analysis of 6,000 cancer samples from 32 datasets showed that all of the considered 20 cancer types exhibit significant age acceleration, with an average of 36 years. Low age-acceleration of cancer tissue is associated with a high number of somatic mutations and TP53 mutations, while mutations in steroid receptors greatly accelerate DNA methylation age in breast cancer. Finally, I characterize the 353 CpG sites that together form an aging clock in terms of chromatin states and tissue variance. Conclusions: I propose that DNA methylation age measures the cumulative effect of an epigenetic maintenance system. This novel epigenetic clock can be used to address a host of questions in developmental biology, cancer and aging research.", 
"Cytosine DNA methylation is a stable epigenetic mark that is crucial for diverse biological processes, including gene and transposon silencing, imprinting and X chromosome inactivation. Recent findings in plants and animals have greatly increased our understanding of the pathways used to accurately target, maintain and modify patterns of DNA methylation and have revealed unanticipated mechanistic similarities between these organisms. Key roles have emerged for small RNAs, proteins with domains that bind methylated DNA and DNA glycosylases in these processes. Drawing on insights from both plants and animals should deepen our understanding of the regulation and biological significance of DNA methylation.", 
"A flexible statistical framework is developed for the analysis of read counts from RNA-Seq gene expression studies. It provides the ability to analyse complex experiments involving multiple treatment conditions and blocking variables while still taking full account of biological variation. Biological variation between RNA samples is estimated separately from the technical variation associated with sequencing technologies. Novel empirical Bayes methods allow each gene to have its own specific variability, even when there are relatively few biological replicates from which to estimate such variability. The pipeline is implemented in the edgeR package of the Bioconductor project. A case study analysis of carcinoma data demonstrates the ability of generalized linear model methods (GLMs) to detect differential expression in a paired design, and even to detect tumour-specific expression changes. The case study demonstrates the need to allow for gene-specific variability, rather than assuming a common dispersion across genes or a fixed relationship between abundance and variability. Genewise dispersions de-prioritize genes with inconsistent results and allow the main analysis to focus on changes that are consistent between biological replicates. Parallel computational approaches are developed to make non-linear model fitting faster and more reliable, making the application of GLMs to genomic data more convenient and practical. Simulations demonstrate the ability of adjusted profile likelihood estimators to return accurate estimators of biological variability in complex situations. When variation is gene-specific, empirical Bayes estimators provide an advantageous compromise between the extremes of assuming common dispersion or separate genewise dispersion. The methods developed here can also be applied to count data arising from DNA-Seq applications, including ChIP-Seq for epigenetic marks and DNA methylation analyses.", 
"Cancer-associated IDH mutations are characterized by neomorphic enzyme activity and resultant 2-hydroxyglutarate (2HG) production. Mutational and epigenetic profiling of a large acute myeloid leukemia (AML) patient cohort revealed that IDH1/2-mutant AMLs display global DNA hypermethylation and a specific hypermethylation signature. Furthermore, expression of 2HG-producing IDH alleles in cells induced global DNA hypermethylation. In the AML cohort, IDH1/2 mutations were mutually exclusive with mutations in the alpha-ketoglutarate-dependent enzyme TET2, and TET2 loss-of-function mutations were associated with similar epigenetic defects as IDH1/2 mutants. Consistent with these genetic and epigenetic data, expression of IDH mutants impaired TET2 catalytic function in cells. Finally, either expression of mutant IDH1/2 or Tet2 depletion impaired hematopoietic differentiation and increased stem/progenitor cell marker expression, suggesting a shared proleukemogenic effect.", 
"The epigenetic regulation of DNA-templated processes has been intensely studied over the last 15 years. DNA methylation, histone modification, nucleosome remodeling, and RNA-mediated targeting regulate many biological processes that are fundamental to the genesis of cancer. Here, we present the basic principles behind these epigenetic pathways and highlight the evidence suggesting that their misregulation can culminate in cancer. This information, along with the promising clinical and preclinical results seen with epigenetic drugs against chromatin regulators, signifies that it is time to embrace the central role of epigenetics in cancer.", 
"DNA methylation is among the best studied epigenetic modifications and is essential to mammalian development. Although the methylation status of most CpG dinucteotides in the genome is stably propagated through mitosis, improvements to methods for measuring methylation have identified numerous regions in which it is dynamically regulated. In this Review, we discuss key concepts in the function of DNA methylation in mammals, stemming from more than two decades of research, including many recent studies that have elucidated when and where DNA methylation has a regulatory role in the genome. We include insights from early development, embryonic stem cells and adult Lineages, particularly haematopoiesis, to highlight the general features of this modification as it participates in both global and localized epigenetic regulation..", 
"Methylation of the N-6 position of adenosine (m(6)A) is a posttranscriptional modification of RNA with poorly understood prevalence and physiological relevance. The recent discovery that FTO, an obesity risk gene, encodes an m(6)A demethylase implicates m(6)A as an important regulator of physiological processes. Here, we present a method for transcriptome-wide m(6)A localization, which combines m(6)A-specific methylated RNA immunoprecipitation with next-generation sequencing (MeRIP-Seq). We use this method to identify mRNAs of 7,676 mammalian genes that contain m(6)A, indicating that m(6)A is a common base modification of mRNA. The m(6)A modification exhibits tissue-specific regulation and is markedly increased throughout brain development. We find that m(6)A sites are enriched near stop codons and in 3' UTRs, and we uncover an association between m 6 A residues and microRNA-binding sites within 3' UTRs. These findings provide a resource for identifying transcripts that are substrates for adenosine methylation and reveal insights into the epigenetic regulation of the mammalian transcriptome.", 
"Chromatin regulators have become attractive targets for cancer therapy, but it is unclear why inhibition of these ubiquitous regulators should have gene-specific effects in tumor cells. Here, we investigate how inhibition of the widely expressed transcriptional coactivator BRD4 leads to selective inhibition of the MYC oncogene in multiple myeloma (MM). BRD4 and Mediator were found to co-occupy thousands of enhancers associated with active genes. They also co-occupied a small set of exceptionally large super-enhancers associated with genes that feature prominently in MM biology, including the MYC oncogene. Treatment of MM tumor cells with the BET-bromodomain inhibitor JQ1 led to preferential loss of BRD4 at super-enhancers and consequent transcription elongation defects that preferentially impacted genes with super-enhancers, including MYC. Super-enhancers were found at key oncogenic drivers in many other tumor cells. These observations have implications for the discovery of cancer therapeutics directed at components of super-enhancers in diverse tumor types.", 
"The ability to measure human aging from molecular profiles has practical implications in many fields, including disease prevention and treatment, forensics, and extension of life. Although chronological age has been linked to changes in DNA methylation, the methylome has not yet been used to measure and compare human aging rates. Here, we build a quantitative model of aging using measurements at more than 450,000 CpG markers from the whole blood of 656 human individuals, aged 19 to 101. This model measures the rate at which an individual's methylome ages, which we show is impacted by gender and genetic variants. We also show that differences in aging rates help explain epigenetic drift and are reflected in the transcriptome. Moreover, we show how our aging model is upheld in other human tissues and reveals an advanced aging rate in tumor tissue. Our model highlights specific components of the aging process and provides a quantitative readout for studying the role of methylation in age-related disease.", 
"Organisms require an appropriate balance of stability and reversibility in gene expression programmes to maintain cell identity or to enable responses to stimuli; epigenetic regulation is integral to this dynamic control. Post-translational modification of histones by methylation is an important and widespread type of chromatin modification that is known to influence biological processes in the context of development and cellular responses. To evaluate how histone methylation contributes to stable or reversible control, we provide a broad overview of how histone methylation is regulated and leads to biological outcomes. The importance of appropriately maintaining or reprogramming histone methylation is illustrated by its links to disease and ageing and possibly to transmission of traits across generations.", 
"Chromosomes are the physical realization of genetic information and thus form the basis for its readout and propagation. Here we present a high-resolution chromosomal contact map derived from a modified genome-wide chromosome conformation capture approach applied to Drosophila embryonic nuclei. The data show that the entire genome is linearly partitioned into well-demarcated physical domains that overlap extensively with active and repressive epigenetic marks. Chromosomal contacts are hierarchically organized between domains. Global modeling of contact density and clustering of domains show that inactive domains are condensed and confined to their chromosomal territories, whereas active domains reach out of the territory to form remote intra-and interchromosomal contacts. Moreover, we systematically identify specific long-range intrachromosomal contacts between Polycomb-repressed domains. Together, these observations allow for quantitative prediction of the Drosophila chromosomal contact map, laying the foundation for detailed studies of chromosome structure and function in a genetically tractable system.", 
"Hybridization has many and varied impacts on the process of speciation. Hybridization may slow or reverse differentiation by allowing gene flow and recombination. It may accelerate speciation via adaptive introgression or cause near-instantaneous speciation by allopolyploidization. It may have multiple effects at different stages and in different spatial contexts within a single speciation event. We offer a perspective on the context and evolutionary significance of hybridization during speciation, highlighting issues of current interest and debate. In secondary contact zones, it is uncertain if barriers to gene flow will be strengthened or broken down due to recombination and gene flow. Theory and empirical evidence suggest the latter is more likely, except within and around strongly selected genomic regions. Hybridization may contribute to speciation through the formation of new hybrid taxa, whereas introgression of a few loci may promote adaptive divergence and so facilitate speciation. Gene regulatory networks, epigenetic effects and the evolution of selfish genetic material in the genome suggest that the DobzhanskyMuller model of hybrid incompatibilities requires a broader interpretation. Finally, although the incidence of reinforcement remains uncertain, this and other interactions in areas of sympatry may have knock-on effects on speciation both within and outside regions of hybridization.", 
"Glioblastoma (GBM) is a brain tumor that carries a dismal prognosis and displays considerable heterogeneity. We have recently identified recurrent H3F3A mutations affecting two critical amino acids (K27 and G34) of histone H3.3 in one-third of pediatric GBM. Here, we show that each H3F3A mutation defines an epigenetic subgroup of GBM with a distinct global methylation pattern, and that they are mutually exclusive with IDH1 mutations, which characterize a third mutation-defined subgroup. Three further epigenetic subgroups were enriched for hallmark genetic events of adult GBM and/or established transcriptomic signatures. We also demonstrate that the two H3F3A mutations give rise to GBMs in separate anatomic compartments, with differential regulation of transcription factors OLIG1, OLIG2, and FOXG1, possibly reflecting different cellular origins.", 
"Epigenetic phenomena in animals and plants are mediated by DNA methylation and stable chromatin modifications. There has been considerable interest in whether environmental factors modulate the establishment and maintenance of epigenetic modifications, and could thereby influence gene expression and phenotype. Chemical pollutants, dietary components, temperature changes and other external stresses can indeed have long-lasting effects on development, metabolism and health, sometimes even in subsequent generations. Although the underlying mechanisms remain largely unknown, particularly in humans, mechanistic insights are emerging from experimental model systems. These have implications for structuring future research and understanding disease and development.", 
"Methylation of cytosine bases in DNA provides a layer of epigenetic control in many eukaryotes that has important implications for normal biology and disease. Therefore, profiling DNA methylation across the genome is vital to understanding the influence of epigenetics. There has been a revolution in DNA methylation analysis technology over the past decade: analyses that previously were restricted to specific loci can now be performed on a genome-scale and entire methylomes can be characterized at single-base-pair resolution. However, there is such a diversity of DNA methylation profiling techniques that it can be challenging to select one. This Review discusses the different approaches and their relative merits and introduces considerations for data analysis.", 
"We have developed a new generation of genome-wide DNA methylation Bead Chip which allows high-throughput methylation profiling of the human genome. The new high density BeadChip can assay over 480K CpG sites and analyze twelve samples in parallel. The innovative content includes coverage of 99% of RefSeq genes with multiple probes per gene, 96% of CpG islands from the UCSC database, CpG island shores and additional content selected from whole-genome bisulfite sequencing data and input from DNA methylation experts. The well-characterized Infinium (R) Assay is used for analysis of CpG methylation using bisulfite-converted genomic DNA. We applied this technology to analyze DNA methylation in normal and tumor DNA samples and compared results with whole-genome bisulfite sequencing (WGBS) data obtained for the same samples. Highly comparable DNA methylation profiles were generated by the array and sequencing methods (average R-2 of 0.95). The ability to determine genome-wide methylation patterns will rapidly advance methylation research. (C) 2011 Elsevier Inc. All rights reserved.", 
"Expression of the INK4b/ARF/INK4a tumor suppressor locus in normal and cancerous cell growth is controlled by methylation of histone H3 at lysine 27 (H3K27me) as directed by the Polycomb group proteins. The antisense noncoding RNA ANRIL of the INK4b/ARF/INK4a locus is also important for expression of the protein-coding genes in cis, but its mechanism has remained elusive. Here we report that chromobox 7 (CBX7) within the polycomb repressive complex 1 binds to ANRIL, and both CBX7 and ANRIL are found at elevated levels in prostate cancer tissues. In concert with H3K27me recognition, binding to RNA contributes to CBX7 function, and disruption of either interaction impacts the ability of CBX7 to repress the INK4b/ARF/INK4a locus and control senescence. Structure-guided analysis reveals the molecular interplay between noncoding RNA and H3K27me as mediated by the conserved chromodomain. Our study suggests a mechanism by which noncoding RNA participates directly in epigenetic transcriptional repression.", 
"Determining how somatic copy number alterations (SCNAs) promote cancer is an important goal. We characterized SCNA patterns in 4,934 cancers from The Cancer Genome Atlas Pan-Cancer data set. Whole-genome doubling, observed in 37% of cancers, was associated with higher rates of every other type of SCNA, TP53 mutations, CCNE1 amplifications and alterations of the PPP2R complex. SCNAs that were internal to chromosomes tended to be shorter than telomere-bounded SCNAs, suggesting different mechanisms underlying their generation. Significantly recurrent focal SCNAs were observed in 140 regions, including 102 without known oncogene or tumor suppressor gene targets and 50 with significantly mutated genes. Amplified regions without known oncogenes were enriched for genes involved in epigenetic regulation. When levels of genomic disruption were accounted for, 7% of region pairs were anticorrelated, and these regions tended to encompass genes whose proteins physically interact, suggesting related functions. These results provide insights into mechanisms of generation and functional consequences of cancer-related SCNAs.", 
"High-throughput technologies are widely used, for example to assay genetic variants, gene and protein expression, and epigenetic modifications. One often overlooked complication with such studies is batch effects, which occur because measurements are affected by laboratory conditions, reagent lots and personnel differences. This becomes a major problem when batch effects are correlated with an outcome of interest and lead to incorrect conclusions. Using both published studies and our own analyses, we argue that batch effects (as well as other technical and biological artefacts) are widespread and critical to address. We review experimental and computational approaches for doing so.", 
"Cytosine methylation is the major covalent modification of mammalian genomic DNA and plays important roles in transcriptional regulation. The molecular mechanism underlying the enzymatic removal of this epigenetic mark, however, remains elusive. Here, we show that 5-methylcytosine (5mC) hydroxylase TET1, by converting 5mCs to 5-hydroxymethylcytosines (5hmCs), promotes DNA demethylation in mammalian cells through a process that requires the base excision repair pathway. Though expression of the 12 known human DNA glycosylases individually did not enhance removal of 5hmCs in mammalian cells, demethylation of both exogenously introduced and endogenous 5hmCs is promoted by the AID (activation-induced deaminase)/APOBEC (apolipoprotein B mRNA-editing enzyme complex) family of cytidine deaminases. Furthermore, Tet1 and Apobec1 are involved in neuronal activity-induced, region-specific, active DNA demethylation and subsequent gene expression in the dentate gyrus of the adult mouse brain in vivo. Our study suggests a TET1-induced oxidation-deamination mechanism for active DNA demethylation in mammals.", 
"Nuclear factor-erythroid 2 p45-related factor 2 (Nrf2, also called Nfe212) is a transcription factor that regulates the cellular redox status. Nrf2 is controlled through a complex transcriptional/epigenetic and post-translational network that ensures its activity increases during redox perturbation, inflammation, growth factor stimulation and nutrient/energy fluxes, thereby enabling the factor to orchestrate adaptive responses to diverse forms of stress. Besides mediating stress-stimulated induction of antioxidant and detoxification genes, Nr12 contributes to adaptation by upregulating the repair and degradation of damaged macromolecules, and by modulating intermediary metabolism. In the latter case, Nrf2 inhibits lipogenesis, supports 0-oxidation of fatty acids, facilitates flux through the pentose phosphate pathway, and increases NADPH regeneration and purine biosynthesis; these observations suggest Nrf2 directs metabolic reprogramming during stress.", 
"Genomes of complex organisms encode an abundance and diversity of long noncoding RNAs (IncRNAs) that are expressed throughout the cell and fulfill a wide variety of regulatory roles at almost every stage of gene expression. These roles, which encompass sensory, guiding, scaffolding and allosteric capacities, derive from folded modular domains in IncRNAs. In this diverse functional repertoire, we focus on the well-characterized ability for IncRNAs to function as epigenetic modulators. Many IncRNAs bind to chromatin-modifying proteins and recruit their catalytic activity to specific sites in the genome, thereby modulating chromatin states and impacting gene expression. Considering this regulatory potential in combination with the abundance of IncRNAs suggests that IncRNAs may be part of a broad epigenetic regulatory network.", 
"Bromodomains (BRDs) are protein interaction modules that specifically recognize epsilon-N-lysine acetylation motifs, a key event in the reading process of epigenetic marks. The 61 BRDs in the human genome cluster into eight families based on structure/sequence similarity. Here, we present 29 high-resolution crystal structures, covering all BRD families. Comprehensive crossfamily structural analysis identifies conserved and family-specific structural features that are necessary for specific acetylation-dependent substrate recognition. Screening of more than 30 representative BRDs against systematic histone-peptide arrays identifies new BRD substrates and reveals a strong influence of flanking posttranslational modifications, such as acetylation and phosphorylation, suggesting that BRDs recognize combinations of marks rather than singly acetylated sequences. We further uncovered a structural mechanism for the simultaneous binding and recognition of diverse diacetyl-containing peptides by BRD4. These data provide a foundation for structure-based drug design of specific inhibitors for this emerging target family.", 
"Epigenetics is one of the most promising and expanding fields in the current biomedical research landscape. Since the inception of epigenetics in the 1940s, the discoveries regarding its implications in normal and disease biology have not stopped, compiling a vast amount of knowledge in the past decade. The field has moved from just one recognized marker, DNA methylation, to a variety of others, including a wide spectrum of histone modifications. From the methodological standpoint, the successful initial single gene candidate approaches have been complemented by the current comprehensive epigenomic approaches that allow the interrogation of genomes to search for translational applications in an unbiased manner. Most important, the discovery of mutations in the epigenetic machinery and the approval of the first epigenetic drugs for the treatment of subtypes of leukemias and lymphomas has been an eye-opener for many biomedical scientists and clinicians. Herein, we will summarize the progress in the field of cancer epigenetics research that has reached mainstream oncology in the development of new biomarkers of the disease and new pharmacological strategies.", 
"Abnormalities of chromosome 7q are common in myeloid malignancies, but no specific target genes have yet been identified. Here, we describe the finding of homozygous EZH2 mutations in 9 of 12 individuals with 7q acquired uniparental disomy. Screening of a total of 614 individuals with myeloid disorders revealed 49 monoallelic or biallelic EZH2 mutations in 42 individuals; the mutations were found most commonly in those with myelodysplastic/myeloproliferative neoplasms (27 out of 219 individuals, or 12%) and in those with myelofibrosis (4 out of 30 individuals, or 13%). EZH2 encodes the catalytic subunit of the polycomb repressive complex 2 (PRC2), a highly conserved histone H3 lysine 27 (H3K27) methyltransferase that influences stem cell renewal by epigenetic repression of genes involved in cell fate decisions. EZH2 has oncogenic activity, and its overexpression has previously been causally linked to differentiation blocks in epithelial tumors. Notably, the mutations we identified resulted in premature chain termination or direct abrogation of histone methyltransferase activity, suggesting that EZH2 acts as a tumor suppressor for myeloid malignancies.", 
"With rare exceptions, spontaneous tumors originate from a single cell. Yet, at the time of clinical diagnosis, the majority of human tumors display startling heterogeneity in many morphological and physiological features, such as expression of cell surface receptors, proliferative and angiogenic potential. To a substantial extent, this heterogeneity might be attributed to morphological and epigenetic plasticity, but there is also strong evidence for the co-existence of genetically divergent tumor cell clones within tumors. In this perspective, we summarize the sources of intra-tumor phenotypic heterogeneity with emphasis on genetic heterogeneity. We review experimental evidence for the existence of both intra-tumor clonal heterogeneity as well as frequent evolutionary divergence between primary tumors and metastatic outgrowths. Furthermore, we discuss potential biological and clinical implications of intra-tumor clonal heterogeneity. (C) 2009 Elsevier B.V. All rights reserved.", 
"Since the human genome was sequenced, the term ``epigenetics'' is increasingly being associated with the hope that we are more than just the sum of our genes. Might what we eat, the air we breathe, or even the emotions we feel influence not only our genes but those of descendants? The environment can certainly influence gene expression and can lead to disease, but transgenerational consequences are another matter. Although the inheritance of epigenetic characters can certainly occur-particularly in plants-how much is due to the environment and the extent to which it happens in humans remain unclear.", 
"The incorporation of histone H3 variants has been implicated in the epigenetic memory of cellular state. Using genome editing with zinc-finger nucleases to tag endogenous H3.3, we report genome-wide profiles of H3 variants in mammalian embryonic stem cells and neuronal precursor cells. Genome-wide patterns of H3.3 are dependent on amino acid sequence and change with cellular differentiation at developmentally regulated loci. The H3.3 chaperone Hira is required for H3.3 enrichment at active and repressed genes. Strikingly, Hira is not essential for localization of H3.3 at telomeres and many transcription factor binding sites. Immunoaffinity purification and mass spectrometry reveal that the proteins Atrx and Daxx associate with H3.3 in a Hira-independent manner. Atrx is required for Hira-independent localization of H3.3 at telomeres and for the repression of telomeric RNA. Our data demonstrate that multiple and distinct factors are responsible for H3.3 localization at specific genomic locations in mammalian cells.", 
"Cyclin-dependent kinases (Cdks) are serine/threonine kinases and their catalytic activities are modulated by interactions with cyclins and Cdk inhibitors (CKIs). Close cooperation between this trio is necessary for ensuring orderly progression through the cell cycle. In addition to their well-established function in cell cycle control, it is becoming increasingly apparent that mammalian Cdks, cyclins and CKIs play indispensable roles in processes such as transcription, epigenetic regulation, metabolism, stem cell self-renewal, neuronal functions and spermatogenesis. Even more remarkably, they can accomplish some of these tasks individually, without the need for Cdk/cyclin complex formation or kinase activity. In this Review, we discuss the latest revelations about Cdks, cyclins and CKIs with the goal of showcasing their functional diversity beyond cell cycle regulation and their impact on development and disease in mammals.", 
"During the course of malignant cancer progression, neoplastic cells undergo dynamic and reversible transitions between multiple phenotypic states, the extremes of which are defined by the expression of epithelial and mesenchymal phenotypes. This plasticity is enabled by underlying shifts in epigenetic regulation. A small cohort of pleiotropically acting transcription factors is widely recognized to effect these shifts by controlling the expression of a constituency of key target genes. These master regulators depend on complex epigenetic regulatory mechanisms, notably the induction of changes in the modifications of chromatin-associated histones, in order to achieve the widespread changes in gene expression observed during epithelial-mesenchymal transitions (EMTs). These associations indicate that an understanding of the functional interactions between such EMT-inducing transcription factors and the modulators of chromatin configuration will provide crucial insights into the fundamental mechanisms underlying cancer progression and may, in the longer term, generate new diagnostic and therapeutic modalities for treating high-grade malignancies.", 
"Despite the success of genome-wide association studies (GWASs) in identifying loci associated with common diseases, a substantial proportion of the causality remains unexplained. Recent advances in genomic technologies have placed us in a position to initiate large-scale studies of human disease-associated epigenetic variation, specifically variation in DNA methylation. Such epigenome-wide association studies (EWASs) present novel opportunities but also create new challenges that are not encountered in GWASs. We discuss EWAS design, cohort and sample selections, statistical significance and power, confounding factors and follow-up studies. We also discuss how integration of EWASs with GWASs can help to dissect complex GWAS haplotypes for functional analysis.", 
"Discoveries over the past decade portend a paradigm shift in molecular biology. Evidence suggests that RNA is not only functional as a messenger between DNA and protein but also involved in the regulation of genome organization and gene expression, which is increasingly elaborate in complex organisms. Regulatory RNA seems to operate at many levels; in particular, it plays an important part in the epigenetic processes that control differentiation and development. These discoveries suggest a central role for RNA in human evolution and ontogeny. Here, we review the emergence of the previously unsuspected world of regulatory RNA from a historical perspective.", 
"DNA methylation, an important type of epigenetic modification in humans, participates in crucial cellular processes, such as embryonic development, X-inactivation, genomic imprinting and chromosome stability. Several platforms have been developed to study genome-wide DNA methylation. Many investigators in the field have chosen the Illumina Infinium HumanMethylation microarray for its ability to reliably assess DNA methylation following sodium bisulfite conversion. Here, we analyzed methylation profiles of 489 adult males and 357 adult females generated by the Infinium HumanMethylation450 microarray. Among the autosomal CpG sites that displayed significant methylation differences between the two sexes, we observed a significant enrichment of cross-reactive probes co-hybridizing to the sex chromosomes with more than 94% sequence identity. This could lead investigators to mistakenly infer the existence of significant autosomal sex-associated methylation. Using sequence identity cutoffs derived from the sex methylation analysis, we concluded that 6% of the array probes can potentially generate spurious signals because of co-hybridization to alternate genomic sequences highly homologous to the intended targets. Additionally, we discovered probes targeting polymorphic CpGs that overlapped SNPs. The methylation levels detected by these probes are simply the reflection of underlying genetic polymorphisms but could be misinterpreted as true signals. The existence of probes that are cross-reactive or of target polymorphic CpGs in the Illumina HumanMethylation microarrays can confound data obtained from such microarrays. Therefore, investigators should exercise caution when significant biological associations are found using these array platforms. A list of all cross-reactive probes and polymorphic CpGs identified by us are annotated in this paper.", 
"Cancer therapy is challenged by the diversity of molecular implementations of oncogenic processes and by the resulting variation in therapeutic responses. Projects such as The Cancer Genome Atlas (TCGA) provide molecular tumor maps in unprecedented detail. The interpretation of these maps remains a major challenge. Here we distilled thousands of genetic and epigenetic features altered in cancers to similar to 500 selected functional events (SFEs). Using this simplified description, we derived a hierarchical classification of 3,299 TCGA tumors from 12 cancer types. The top classes are dominated by either mutations (M class) or copy number changes (C class). This distinction is clearest at the extremes of genomic instability, indicating the presence of different oncogenic processes. The full hierarchy shows functional event patterns characteristic of multiple cross-tissue groups of tumors, termed oncogenic signature classes. Targetable functional events in a tumor class are suggestive of class-specific combination therapy. These results may assist in the definition of clinical trials to match actionable oncogenic signatures with personalized therapies.", 
"DNA methylation is one of the best-characterized epigenetic modifications and has been implicated in numerous biological processes, including transposable element silencing, genomic imprinting and X chromosome inactivation. Compared with other epigenetic modifications, DNA methylation is thought to be relatively stable. Despite its role in long-term silencing, DNA methylation is more dynamic than originally thought as active DNA demethylation has been observed during specific stages of development. In the past decade, many enzymes have been proposed to carry out active DNA demethylation and growing evidence suggests that, depending on the context, this process may be achieved by multiple mechanisms. Insight into how DNA methylation is dynamically regulated will broaden our understanding of epigenetic regulation and have great implications in somatic cell reprogramming and regenerative medicine.", 
"DNA methylation is one of the most intensely studied epigenetic modifications in mammals. In normal cells, it assures the proper regulation of gene expression and stable gene silencing. DNA methylation is associated with histone modifications and the interplay of these epigenetic modifications is crucial to regulate the functioning of the genome by changing chromatin architecture. The covalent addition of a methyl group occurs generally in cytosine within CpG dinucleotides which are concentrated in large clusters called CpG islands. DNA methyltransferases are responsible for establishing and maintenance of methylation pattern. It is commonly known that inactivation of certain tumor-suppressor genes occurs as a consequence of hypermethylation within the promoter regions and a numerous studies have demonstrated a broad range of genes silenced by DNA methylation in different cancer types. On the other hand, global hypomethylation, inducing genomic instability, also contributes to cell transformation. Apart from DNA methylation alterations in promoter regions and repetitive DNA sequences, this phenomenon is associated also with regulation of expression of noncoding RNAs such as microRNAs that may play role in tumor suppression. DNA methylation seems to be promising in putative translational use in patients and hypermethylated promoters may serve as biomarkers. Moreover, unlike genetic alterations, DNA methylation is reversible what makes it extremely interesting for therapy approaches. The importance of DNA methylation alterations in tumorigenesis encourages us to decode the human epigenome. Different DNA methylome mapping techniques are indispensable to realize this project in the future. (C) 2010, Elsevier Inc.", 
"Epigenetic information can be inherited through the mammalian germline and represents a plausible transgenerational carrier of environmental information. To test whether transgenerational inheritance of environmental information occurs in mammals, we carried out an expression profiling screen for genes in mice that responded to paternal diet. Offspring of males fed a low-protein diet exhibited elevated hepatic expression of many genes involved in lipid and cholesterol biosynthesis and decreased levels of cholesterol esters, relative to the offspring of males fed a control diet. Epigenomic profiling of offspring livers revealed numerous modest (similar to 20%) changes in cytosine methylation depending on paternal diet, including reproducible changes in methylation over a likely enhancer for the key lipid regulator Ppara. These results, in conjunction with recent human epidemiological data, indicate that parental diet can affect cholesterol and lipid metabolism in offspring and define a model system to study environmental reprogramming of the heritable epigenome.", 
"Induction of cell death and inhibition of cell survival are the main principles of cancer therapy. Resistance to chemotherapeutic agents is a major problem in oncology, which limits the effectiveness of anticancer drugs. A variety of factors contribute to drug resistance, including host factors, specific genetic or epigenetic alterations in the cancer cells and so on. Although various mechanisms by which cancer cells become resistant to anticancer drugs in the microenvironment have been well elucidated, how to circumvent this resistance to improve anticancer efficacy remains to be defined. Autophagy, an important homeostatic cellular recycling mechanism, is now emerging as a crucial player in response to metabolic and therapeutic stresses, which attempts to maintain/restore metabolic homeostasis through the catabolic lysis of excessive or unnecessary proteins and injured or aged organelles. Recently, several studies have shown that autophagy constitutes a potential target for cancer therapy and the induction of autophagy in response to therapeutics can be viewed as having a prodeath or a prosurvival role, which contributes to the anticancer efficacy of these drugs as well as drug resistance. Thus, understanding the novel function of autophagy may allow us to develop a promising therapeutic strategy to enhance the effects of chemotherapy and improve clinical outcomes in the treatment of cancer patients.", 
"DNA methylation is a critical epigenetic regulator in mammalian development. Here, we present a whole-genome comparative view of DNA methylation using bisulfite sequencing of three cultured cell types representing progressive stages of differentiation: human embryonic stem cells (hESCs), a fibroblastic differentiated derivative of the hESCs, and neonatal fibroblasts. As a reference, we compared our maps with a methylome map of a fully differentiated adult cell type, mature peripheral blood mononuclear cells (monocytes). We observed many notable common and cell-type-specific features among all cell types. Promoter hypomethylation (both CG and CA) and higher levels of gene body methylation were positively correlated with transcription in all cell types. Exons were more highly methylated than introns, and sharp transitions of methylation occurred at exon-intron boundaries, suggesting a role for differential methylation in transcript splicing. Developmental stage was reflected in both the level of global methylation and extent of non-CpG methylation, with hESC highest, fibroblasts intermediate, and monocytes lowest. Differentiation-associated differential methylation profiles were observed for developmentally regulated genes, including the HOX clusters, other homeobox transcription factors, and pluripotence-associated genes such as POU5F1, TCF3, and KLF4. Our results highlight the value of high-resolution methylation maps, in conjunction with other systems-level analyses, for investigation of previously undetectable developmental regulatory mechanisms.", 
"RNA-directed DNA methylation (RdDM) is the major small RNA-mediated epigenetic pathway in plants. RdDM requires a specialized transcriptional machinery that comprises two plant-specific RNA polymerases - Pot IV and Pot V - and a growing number of accessory proteins, the functions of which in the RdDM mechanism are only partially understood. Recent work has revealed variations in the canonical RdDM pathway and identified factors that recruit Pot IV and Pol V to specific target sequences. RdDM, which transcriptionally represses a subset of transposons and genes, is implicated in pathogen defence, stress responses and reproduction, as well as in interallelic and intercellular communication.", 
"Tumor heterogeneity is a major barrier to effective cancer diagnosis and treatment. We recently identified cancer-specific differentially DNA-methylated regions (cDMRs) in colon cancer, which also distinguish normal tissue types from each other, suggesting that these cDMRs might be generalized across cancer types. Here we show stochastic methylation variation of the same cDMRs, distinguishing cancer from normal tissue, in colon, lung, breast, thyroid and Wilms' tumors, with intermediate variation in adenomas. Whole-genome bisulfite sequencing shows these variable cDMRs are related to loss of sharply delimited methylation boundaries at CpG islands. Furthermore, we find hypomethylation of discrete blocks encompassing half the genome, with extreme gene expression variability. Genes associated with the cDMRs and large blocks are involved in mitosis and matrix remodeling, respectively. We suggest a model for cancer involving loss of epigenetic stability of well-defined genomic domains that underlies increased methylation variability in cancer that may contribute to tumor heterogeneity.", 
"Emergence of form and function during embryogenesis arises in large part through cell-type- and cell-state-specific variation in gene expression patterns, mediated by specialized cis-regulatory elements called enhancers. Recent large-scale epigenomic mapping revealed unexpected complexity and dynamics of enhancer utilization patterns, with 400,000 putative human enhancers annotated by the ENCODE project alone. These large-scale efforts were largely enabled through the understanding that enhancers share certain stereotypical chromatin features. However, an important question still lingers: what is the functional significance of enhancer chromatin modification? Here we give an overview of enhancer-associated modifications of histones and DNA and discuss enzymatic activities involved in their dynamic deposition and removal. We describe potential downstream effectors of these marks and propose models for exploring functions of chromatin modification in regulating enhancer activity during development.", 
"The generation of properly functioning gametes in vitro requires reconstitution of the multistepped pathway of germ cell development. We demonstrate here the generation of primordial germ cell-like cells (PGCLCs) in mice with robust capacity for spermatogenesis. PGCLCs were generated from embryonic stem cells (ESCs) and induced pluripotent stem cells (iPSCs) through epiblast-like cells (EpiLCs), a cellular state highly similar to pregastrulating epiblasts but distinct from epiblast stem cells (EpiSCs). Reflecting epiblast development, EpiLC induction from ESCs/iPSCs is a progressive process, and EpiLCs highly competent for the PGC fate are a transient entity. The global transcription profiles, epigenetic reprogramming, and cellular dynamics during PGCLC induction from EpiLCs meticulously capture those associated with PGC specification from the epiblasts. Furthermore, we identify Integrin-beta 3 and SSEA1 as markers that allow the isolation of PGCLCs with spermatogenic capacity from tumorigenic undifferentiated cells. Our findings provide a paradigm for the first step of in vitro gametogenesis.", 
"Observational epidemiological studies are prone to confounding, reverse causation and various biases and have generated findings that have proved to be unreliable indicators of the causal effects of modifiable exposures on disease outcomes. Mendelian randomization (MR) is a method that utilizes genetic variants that are robustly associated with such modifiable exposures to generate more reliable evidence regarding which interventions should produce health benefits. The approach is being widely applied, and various ways to strengthen inference given the known potential limitations of MR are now available. Developments of MR, including two-sample MR, bidirectional MR, network MR, two-step MR, factorial MR and multiphenotype MR, are outlined in this review. The integration of genetic information into population-based epidemiological studies presents translational opportunities, which capitalize on the investment in genomic discovery research.", 
"Successful reprogramming of differentiated human somatic cells into a pluripotent state would allow creation of patient- and disease-specific stem cells. We previously reported generation of induced pluripotent stem (iPS) cells, capable of germline transmission, from mouse somatic cells by transduction of four defined transcription factors. Here, we demonstrate the generation of iPS cells from adult human dermal fibroblasts with the same four factors: Oct3/4, Sox2, Klf4, and c-Myc. Human iPS cells were similar to human embryonic stem (ES) cells in morphology, proliferation, surface antigens, gene expression, epigenetic status of pluripotent cell-specific genes, and telomerase activity. Furthermore, these cells could differentiate into cell types of the three germ layers in vitro and in teratomas. These findings demonstrate that iPS cells can be generated from adult human fibroblasts.", 
"The most highly conserved noncoding elements (HCNEs) in mammalian genomes cluster within regions enriched for genes encoding developmentally important transcription factors (TFs). This suggests that HCNE-rich regions may contain key regulatory controls involved in development. We explored this by examining histone methylation in mouse embryonic stem (ES) cells across 56 large HCNE-rich loci. We identified a specific modification pattern, termed bivalent domains, consisting of large regions of H3 lysine 27 methylation harboring smaller regions of H3 lysine 4 methylation. Bivalent domains tend to coincide with TF genes expressed at low levels. We propose that bivalent domains silence developmental genes in ES cells while keeping them poised for activation. We also found striking correspondences between genome sequence and histone methylation in ES cells, which become notably weaker in differentiated cells. These results highlight the importance of DNA sequence in defining the initial epigenetic landscape and suggest a novel chromatin-based mechanism for maintaining pluripotency.", 
"RNA is not only a messenger operating between DNA and protein. Transcription of essentially the entire eukaryotic genome generates a myriad of non-protein-coding RNA species that show complex overlapping patterns of expression and regulation. Although long noncoding RNAs (lncRNAs) are among the least well-understood of these transcript species, they cannot all be dismissed as merely transcriptional noise.'' Here, we review the evolution of lncRNAs and their roles in transcriptional regulation, epigenetic gene regulation, and disease.", 
"Noncoding RNAs (ncRNA) participate in epigenetic regulation but are poorly understood. Here we characterize the transcriptional landscape of the four human HOX loci at five base pair resolution in 11 anatomic sites and identify 231 HOX ncRNAs that extend known transcribed regions by more than 30 kilobases. HOX ncRNAs are spatially expressed along developmental axes and possess unique sequence motifs, and their expression demarcates broad chromosomal domains of differential histone methylation and RNA polymerase accessibility. We identified a 2.2 kilobase ncRNA residing in the HOXC locus, termed HOTAIR, which represses transcription in trans across 40 kilobases of the HOXD locus. HOTAIR interacts with Polycomb Repressive Complex 2 (PRC2) and is required for PRC2 occupancy and histone H3 lysine-27 trimethylation of HOXD locus. Thus, transcription of ncRNA may demarcate chromosomal domains of gene silencing at a distance; these results have broad implications for gene regulation in development and disease states.", 
"Over the past several years it has become clear that alterations in the expression of microRNA (miRNA) genes contribute to the pathogenesis of most - if not all - human malignancies. These alterations can be caused by various mechanisms, including deletions, amplifications or mutations involving miRNA loci, epigenetic silencing or the dysregulation of transcription factors that target specific miRNAs. Because malignant cells show dependence on the dysregulated expression of miRNA genes, which in turn control or are controlled by the dysregulation of multiple protein-coding oncogenes or tumour suppressor genes, these small RNAs provide important opportunities for the development of future miRNA-based therapies.", 
"The genomes of many animals, plants and fungi are tagged by methylation of DNA cytosine. To understand the biological significance of this epigenetic mark it is essential to know where in the genome it is located. New techniques are making it easier to map DNA methylation patterns on a large scale and the results have already provided surprises. In particular, the conventional view that DNA methylation functions predominantly to irreversibly silence transcription is being challenged. Not only is promoter methylation often highly dynamic during development, but many organisms also seem to target DNA methylation specifically to the bodies of active genes.", 
"DNA methylation is a crucial epigenetic modification of the genome that is involved in regulating many cellular processes. These include embryonic development, transcription, chromatin structure, X chromosome inactivation, genomic imprinting and chromosome stability. Consistent with these important roles, a growing number of human diseases have been found to be associated with aberrant DNA methylation. The study of these diseases has provided new and fundamental insights into the roles that DNA methylation and other epigenetic modifications have in development and normal cellular homeostasis.", 
"Methylation of DNA at position five of the cytosine ring occurs at most CpG dinucleotides in the mammalian genome and is essential for embryonic viability. With several of the key proteins now known, it has become possible to approach the biological significance of this epigenetic system through both biochemistry and genetics. As a result, advances have been made in our understanding of the mechanisms by which DNA methylation is targeted to specific regions of the genome and interpreted by methyl-CpG-binding proteins. Recent studies have illuminated the role of DNA methylation in controlling gene expression and have strengthened its links with histone modification and chromatin remodelling.", 
"Epidemiological evidence increasingly suggests that environmental exposures early in development have a role in susceptibility to disease in later life. In addition, some of these environmental effects seem to be passed on through subsequent generations. Epigenetic modifications provide a plausible link between the environment and alterations in gene expression that might lead to disease phenotypes. An increasing body of evidence from animal studies supports the role of environmental epigenetics in disease susceptibility. Furthermore, recent studies have demonstrated for the first time that heritable environmentally induced epigenetic modifications underlie reversible transgenerational alterations in phenotype. Methods are now becoming available to investigate the relevance of these phenomena to human disease.", 
"Deciphering the multiple layers of epigenetic regulation that control transcription is critical to understanding how plants develop and respond to their environment. Using sequencing-by-synthesis technology we directly sequenced the cytosine methylome (methylC-seq), transcriptome (mRNA-seq), and small RNA transcriptome (smRNA-seq) to generate highly integrated epigenome maps for wild-type Arabidopsis thaliana and mutants defective in DNA methyltransferase or demethylase activity. At singlebase resolution we discovered extensive, previously undetected DNA methylation, identified the context and level of methylation at each site, and observed local sequence effects upon methylation state. Deep sequencing of smRNAs revealed a direct relationship between the location of smRNAs and DNA methylation, perturbation of smRNA biogenesis upon loss of CpG DNA methylation, and a tendency for smRNAs to direct strand-specific DNA methylation in regions of RNA-DNA homology. Finally, strandspecific mRNA-seq revealed altered transcript abundance of hundreds of genes, transposons, and unannotated intergenic transcripts upon modification of the DNA methylation state.", 
"Plants and animals use small RNAs (microRNAs [miRNAs] and siRNAs) as guides for posttranscriptional and epigenetic regulation. In plants, miRNAs and trans-acting (ta) siRNAs form through distinct biogenesis pathways, although they both interact with target transcripts and guide cleavage. An integrated approach to identify targets of Arabidopsis thaliana miRNAs and ta-siRNAs revealed several new classes of small RNA-regulated genes, including conventional genes such as Argonaute2 and an E2-ubiquitin conjugating enzyme. Surprisingly, five tasiRNA-generating transcripts were identified as targets of miR173 or miR390. Rather than functioning as negative regulators, miR173- and miR390-guided cleavage was shown to set the 21-nucleotide phase for ta-siRNA precursor processing. These data support a model in which miRNA-guided formation of a 5' or 3' terminus within pre-ta-siRNA transcripts, followed by RDR6-dependent formation of dsRNA and Dicer-like processing, yields phased ta-siRNAs that negatively regulate other genes.", 
"For the past 25 years, it has been known that alterations in DNA methylation (DNAm) occur in cancer, including hypomethylation of oncogenes and hypermethylation of tumor suppressor genes. However, most studies of cancer methylation have assumed that functionally important DNAm will occur in promoters, and that most DNAm changes in cancer occur in CpG islands. Here we show that most methylation alterations in colon cancer occur not in promoters, and also not in CpG islands, but in sequences up to 2 kb distant, which we term 'CpG island shores'. CpG island shore methylation was strongly related to gene expression, and it was highly conserved in mouse, discriminating tissue types regardless of species of origin. There was a notable overlap (45-65%) of the locations of colon cancer-related methylation changes with those that distinguished normal tissues, with hypermethylation enriched closer to the associated CpG islands, and hypomethylation enriched further from the associated CpG island and resembling that of noncolon normal tissues. Thus, methylation changes in cancer are at sites that vary normally in tissue differentiation, consistent with the epigenetic progenitor model of cancer, which proposes that epigenetic alterations affecting tissue-specific differentiation are the predominant mechanism by which epigenetic changes cause cancer.", 
"An altered pattern of epigenetic modifications is central to many common human diseases, including cancer. Many studies have explored the mosaic patterns of DNA methylation and histone modification in cancer cells on a gene-by-gene basis; among their results has been the seminal finding of transcriptional silencing of tumour-suppressor genes by CpG-island-promoter hypermethylation. However, recent technological advances are now allowing cancer epigenetics to be studied genome-wide-an approach that has already begun to provide both biological insight and new avenues for translational research. It is time to 'upgrade' cancer epigenetics research and put together an ambitious plan to tackle the many unanswered questions in this field using epigenomics approaches.", 
"The term non-coding RNA (ncRNA) is commonly employed for RNA that does not encode a protein, but this does not mean that such RNAs do not contain information nor have function. Although it has been generally assumed that most genetic information is transacted by proteins, recent evidence suggests that the majority of the genomes of mammals and other complex organisms is in fact transcribed into ncRNAs, many of which are alternatively spliced and/or processed into smaller products. These ncRNAs include microRNAs and snoRNAs (many if not most of which remain to be identified), as well as likely other classes of yet-to-be-discovered small regulatory RNAs, and tens of thousands of longer transcripts (including complex patterns of interlacing and overlapping sense and antisense transcripts), most of whose functions are unknown. These RNAs (including those derived from introns) appear to comprise a hidden layer of internal signals that control various levels of gene expression in physiology and development, including chromatin architecture/epigenetic memory, transcription, RNA splicing, editing, translation and turnover. RNA regulatory networks may determine most of our complex characteristics, play a significant role in disease and constitute an unexplored world of genetic variation both within and between species.", 
" ", 
"X-chromosome inactivation is the mammalian dosage compensation mechanism by which transcription of X-linked genes is equalized between females and males. In an N-ethyl-N-nitrosourea (ENU) mutagenesis screen on mice for modifiers of epigenetic reprogramming, we identified the MommeD1 (modifier of murine metastable epialleles) mutation as a semidominant suppressor of variegation. MommeD1 shows homozygous female-specific mid-gestation lethality and hypomethylation of the X-linked gene Hprt1, suggestive of a defect in X inactivation(1). Here we report that the causative point mutation lies in a previously uncharacterized gene, Smchd1 (structural maintenance of chromosomes hinge domain containing 1). We find that SmcHD1 is not required for correct Xist expression, but localizes to the inactive X and has a role in the maintenance of X inactivation and the hypermethylation of CpG islands associated with the inactive X. This finding links a group of proteins normally associated with structural aspects of chromosome biology with epigenetic gene silencing.", 
" ", 
"The packaging of chromosomal DNA by nucleosomes condenses and organizes the genome, but occludes many regulatory DNA elements. However, this constraint also allows nucleosomes and other chromatin components to actively participate in the regulation of transcription, chromosome segregation, DNA replication, and DNA repair. To enable dynamic access to packaged DNA and to tailor nucleosome composition in chromosomal regions, cells have evolved a set of specialized chromatin remodeling complexes (remodelers). Remodelers use the energy of ATP hydrolysis to move, destabilize, eject, or restructure nucleosomes. Here, we address many aspects of remodeler biology: their targeting, mechanism, regulation, shared and unique properties, and specialization for particular biological processes. We also address roles for remodelers in development, cancer, and human syndromes.", 
"Ectopic expression of the four transcription factors Oct4, Sox2, c-Myc, and Klf4 is sufficient to confer a pluripotent state upon the fibroblast genome, generating induced pluripotent stem (PS) cells. It remains unknown if nuclear reprogramming induced by these four factors globally resets epigenetic differences between differentiated and pluripotent cells. Here, using novel selection approaches, we have generated PS cells from fibroblasts to characterize their epigenetic state. Female PS cells showed reactivation of a somatically silenced X chromosome and underwent random X inactivation upon differentiation. Genome-wide analysis of two key histone modifications indicated that PS cells are highly similar to ES cells. Consistent with these observations, PS cells gave rise to viable high-degree chimeras with contribution to the germline. These data show that transcription factor-induced reprogramming leads to the global reversion of the somatic epigenome into an ES-like state. Our results provide a paradigm for studying the epigenetic modifications that accompany nuclear reprogramming and suggest that abnormal epigenetic reprogramming does not pose a problem for the potential therapeutic applications of PS cells.", 
"Cancer is widely perceived as a heterogeneous group of disorders with markedly different biological properties, which are caused by a series of clonally selected genetic changes in key tumour-suppressor genes and oncogenes. However, recent data suggest that cancer has a fundamentally common basis that is grounded in a polyclonal epigenetic disruption of stem/progenitor cells, mediated by 'tumour-progenitor genes'. Furthermore, tumour cell heterogeneity is due in part to epigenetic variation in progenitor cells, and epigenetic plasticity together with genetic lesions drives tumour progression. This crucial early role for epigenetic alterations in cancer is in addition to epigenetic alterations that can substitute for genetic variation later in tumour progression. Therefore, non-neoplastic but epigenetically disrupted stem/progenitor cells might be a crucial target for cancer risk assessment and chemoprevention.", 
"Polyploids - organisms that have multiple sets of chromosomes - are common in certain plant and animal taxa, and can be surprisingly stable. The evidence that has emerged from genome analyses also indicates that many other eukaryotic genomes have a polyploid ancestry, suggesting that both humans and most other eukaryotes have either benefited from or endured polyploidy. Studies of polyploids soon after their formation have revealed genetic and epigenetic interactions between redundant genes. These interactions can be related to the phenotypes and evolutionary fates of polyploids. Here, I consider the advantages and challenges of polyploidy, and its evolutionary potential.", 
"CpG island hypermethylation and global genomic hypomethylation are common epigenetic features of cancer cells. Less attention has been focused on histone modifications in cancer cells. We characterized post-translational modifications to histone H4 in a comprehensive panel of normal tissues, cancer cell lines and primary tumors. Using immunodetection, high-performance capillary electrophoresis and mass spectrometry, we found that cancer cells had a loss of monoacetylated and trimethylated forms of histone H4. These changes appeared early and accumulated during the tumorigenic process, as we showed in a mouse model of multistage skin carcinogenesis. The losses occurred predominantly at the acetylated Lys16 and trimethylated Lys20 residues of histone H4 and were associated with the hypomethylation of DNA repetitive sequences, a well-known characteristic of cancer cells. Our data suggest that the global loss of monoacetylation and trimethylation of histone H4 is a common hallmark of human tumor cells.", 
"Cytosine methylation is required for mammalian development and is often perturbed in human cancer. To determine how this epigenetic modification is distributed in the genomes of primary and transformed cells, we used an immunocapturing approach followed by DNA microarray analysis to generate methylation profiles of all human chromosomes at 80-kb resolution and for a large set of CpG islands. In primary cells we identified broad genomic regions of differential methylation with higher levels in gene-rich neighborhoods. Female and male cells had indistinguishable profiles for autosomes but differences on the X chromosome. The inactive X chromosome ( Xi) was hypermethylated at only a subset of gene-rich regions and, unexpectedly, overall hypomethylated relative to its active counterpart. The chromosomal methylation profile of transformed cells was similar to that of primary cells. Nevertheless, we detected large genomic segments with hypomethylation in the transformed cell residing in gene-poor areas. Furthermore, analysis of 6,000 CpG islands showed that only a small set of promoters was methylated differentially, suggesting that aberrant methylation of CpG island promoters in malignancy might be less frequent than previously hypothesized.", 
"Inheritance requires genome duplication, reproduction of chromatin and its epigenetic information, mechanisms to ensure genome integrity, and faithful transmission of the information to progeny. Proliferating cell nuclear antigen (PCNA)-a cofactor of DNA polymerases that encircles DNA-orchestrates several of these functions by recruiting crucial players to the replication fork. Remarkably, many factors that are involved in replication-linked processes interact with a particular face of PCNA and through the same interaction domain, indicating that these interactions do not occur simultaneously during replication. Switching of PCNA partners may be triggered by affinity-driven competition, phosphorylation, proteolysis, and modification of PCNA by ubiquitin and SUMO.", 
"Cytosine methylation is important for transposon silencing and epigenetic regulation of endogenous genes, although the extent to which this DNA modification functions to regulate the genome is still unknown. Here we report the first comprehensive DNA methylation map of an entire genome, at 35 base pair resolution, using the flowering plant Arabidopsis thaliana as a model. We find that pericentromeric heterochromatin, repetitive sequences, and regions producing small interfering RNAs are heavily methylated. Unexpectedly, over one-third of expressed genes contain methylation within transcribed regions, whereas only similar to 5% of genes show methylation within promoter regions. Interestingly, genes methylated in transcribed regions are highly expressed and constitutively active, whereas promoter-methylated genes show a greater degree of tissue-specific expression. Whole-genome tiling-array transcriptional profiling of DNA methyltransferase null mutants identified hundreds of genes and intergenic noncoding RNAs with altered expression levels, many of which may be epigenetically controlled by DNA methylation.", 
"Overlapping epigenetic mechanisms have evolved in eukaryotic cells to silence the expression and mobility of transposable elements (TEs). Owing to their ability to recruit the silencing machinery, TEs have served as building blocks for epigenetic phenomena, both at the level of single genes and across larger chromosomal regions. Important progress has been made recently in understanding these silencing mechanisms. In addition, new insights have been gained into how this silencing has been co-opted to serve essential functions in 'host' cells, highlighting the importance of TEs in the epigenetic regulation of the genome.", 
"Cellular senescence, a state of irreversible growth arrest, can be triggered by multiple mechanisms including telomere shortening, the epigenetic derepression of the INK4a/ARF locus, and DNA damage. Together these mechanisms limit excessive or aberrant cellular proliferation, and so the state of senescence protects against the development of cancer. Recent evidence suggests that cellular senescence also may be involved in aging.", 
"Histones comprise the major protein component of chromatin, the scaffold in which the eukaryotic genome is packaged, and are subject to many types of post-translational modifications (PTMs), especially on their flexible tails. These modifications may constitute a 'histone code' and could be used to manage epigenetic information that helps extend the genetic message beyond DNA sequences. This proposed code, read in part by histone PTM-binding 'effector' modules and their associated complexes, is predicted to define unique functional states of chromatin and/or regulate various chromatin-templated processes. A wealth of structural and functional data show how chromatin effector modules target their cognate covalent histone modifications. Here we summarize key features in molecular recognition of histone PTMs by a diverse family of 'reader pockets', highlighting specific readout mechanisms for individual marks, common themes and insights into the downstream functional consequences of the interactions. Changes in these interactions may have far-reaching implications for human biology and disease, notably cancer.", 
"Chromatin immunoprecipitation followed by sequencing (ChIP-seq) is a technique for genome-wide profiling of DNA-binding proteins, histone modifications or nucleosomes. Owing to the tremendous progress in next-generation sequencing technology, ChIP-seq offers higher resolution, less noise and greater coverage than its array-based predecessor ChIP-chip. With the decreasing cost of sequencing, ChIP-seq has become an indispensable tool for studying gene regulation and epigenetic mechanisms. In this Review, I describe the benefits and challenges in harnessing this technique with an emphasis on issues related to experimental design and data analysis. ChIP-seq experiments generate large quantities of data, and effective computational analysis will be crucial for uncovering biological mechanisms.", 
"Inflammation is linked clinically and epidemiologically to cancer, and NF-kappa B appears to play a causative role, but the mechanisms are poorly understood. We show that transient activation of Src oncoprotein can mediate an epigenetic switch from immortalized breast cells to a stably transformed line that forms self-renewing mammospheres that contain cancer stem cells. Src activation triggers an inflammatory response mediated by NF-kappa B that directly activates Lin28 transcription and rapidly reduces let-7 microRNA levels. Let-7 directly inhibits IL6 expression, resulting in higher levels of IL6 than achieved by NF-kappa B activation. IL6-mediated activation of the STAT3 transcription factor is necessary for transformation, and IL6 activates NF-kappa B, thereby completing a positive feedback loop. This regulatory circuit operates in other cancer cells lines, and its transcriptional signature is found in human cancer tissues. Thus, inflammation activates a positive feedback loop that maintains the epigenetic transformed state for many generations in the absence of the inducing signal.", 
"Expression profiling of T24 cells revealed that 17 out of 313 human miRNAs were upregulated more than 3-fold by simultaneous treatment with the chromatin-modifying drugs 5-aza-2'-deoxycytidine and 4-phenylbutyric acid. One of these, miR-127, is embedded in a CpG island and is highly induced from its own promoter after treatment. miR-127 is usually expressed as part of a miRNA cluster in normal cells but not in cancer cells, suggesting that it is subject to epigenetic silencing. In addition, the proto-oncogene BCL6, a potential target of miR-127, was translationally downregulated after treatment. These results suggest that DNA demethylation and histone deacetylase inhibition can activate expression of miRNAs that may act as tumor suppressors.", 
"Polycomb proteins form chromatin-modifying complexes that implement transcriptional silencing in higher eukaryotes. Hundreds of genes are silenced by Polycomb proteins, including dozens of genes that encode crucial developmental regulators in organisms ranging from plants to humans. Two main families of complexes, called Polycomb repressive complex 1 (PRC1) and PRC2, are targeted to repressed regions. Recent studies have advanced our understanding of these complexes, including their potential mechanisms of gene silencing, the roles of chromatin modifications, their means of delivery to target genes and the functional distinctions among variant complexes. Emerging concepts include the existence of a Polycomb barrier to transcription elongation and the involvement of non-coding RNAs in the targeting of Polycomb complexes. These findings have an impact on the epigenetic programming of gene expression in many biological systems.", 
"A recent meeting (December 2008) regarding chromatin-based epigenetics was hosted by the Banbury Conference Center and Cold Spring Harbor Laboratory. The intent was to discuss aspects of epigenetic control of genomic function, and to arrive at a consensus definition of epigenetics'' to be considered by the broader community. It was evident that multiple mechanistic steps lead to the stable heritance of the epigenetic phenotype. Below we provide our view and interpretation of the proceedings at the meeting.", 
"Epigenetic genome modifications are thought to be important for specifying the lineage and developmental stage of cells within a multicellular organism. Here, we show that the epigenetic profile of pluripotent embryonic stem cells (ES) is distinct from that of embryonic carcinoma cells, haematopoietic stem cells (HSC) and their differentiated progeny. Silent, lineage-specific genes replicated earlier in pluripotent cells than in tissue-specific stem cells or differentiated cells and had unexpectedly high levels of acetylated H3K9 and methylated H3K4. Unusually, in ES cells these markers of open chromatin were also combined with H3K27 trimethylation at some non-expressed genes. Thus, pluripotency of ES cells is characterized by a specific epigenetic profile where lineage-specific genes may be accessible but, if so, carry repressive H3K27 trimethylation modifications. H3K27 methylation is functionally important for preventing expression of these genes in ES cells as premature expression occurs in embryonic ectoderm development (Eed)-deficient ES cells. Our data suggest that lineage-specific genes are primed for expression in ES cells but are held in check by opposing chromatin modifications.", 
"DNA methylation is the most stable type of epigenetic modification modulating the transcriptional plasticity of mammalian genomes. Using bisulfite DNA sequencing, we report high-resolution methylation profiles of human chromosomes 6, 20 and 22, providing a resource of about 1.9 million CpG methylation values derived from 12 different tissues. Analysis of six annotation categories showed that evolutionarily conserved regions are the predominant sites for differential DNA methylation and that a core region surrounding the transcriptional start site is an informative surrogate for promoter methylation. We find that 17% of the 873 analyzed genes are differentially methylated in their 5 ' UTRs and that about one-third of the differentially methylated 5 ' UTRs are inversely correlated with transcription. Despite the fact that our study controlled for factors reported to affect DNA methylation such as sex and age, we did not find any significant attributable effects. Our data suggest DNA methylation to be ontogenetically more stable than previously thought.", 
"The Polycomb group (PcG) proteins form chromatin-modifying complexes that are essential for embryonic development and stem cell renewal and are commonly deregulated in cancer. Here, we identify their target genes using genome-wide location analysis in human embryonic fibroblasts. We find that Polycomb-Repressive Complex I (PRC1), PRC2, and tri-methylated histone H3K27 co-occupy > 1000 silenced genes with a strong functional bias for embryonic development and cell fate decisions. We functionally identify 40 genes derepressed in human embryonic fibroblasts depleted of the PRC2 components (EZH2, EED, SUZ12) and the PRC1 component, BMI-1. Interestingly, several markers of osteogenesis, adipogenesis, and chrondrogenesis are among these genes, consistent with the mesenchymal origin of fibroblasts. Using a neuronal model of differentiation, we delineate two different mechanisms for regulating PcG target genes. For genes activated during differentiation, PcGs are displaced. However, for genes repressed during differentiation, we paradoxically find that they are already bound by the PcGs in nondifferentiated cells despite being actively transcribed. Our results are consistent with the hypothesis that PcGs are part of a preprogrammed memory system established during embryogenesis marking certain key genes for repressive signals during subsequent developmental and differentiation processes.", 
"Epigenetic marking systems confer stability of gene expression during mammalian development. Genome-wide epigenetic reprogramming occurs at stages when developmental potency of cells changes. At fertilization, the paternal genome exchanges protamines for histones, undergoes DNA demethylation, and acquires histone modifications, whereas the maternal genome appears epigenetically more static. During preimplantation development, there is passive DNA demethylation and further reorganization of histone modifications. In blastocysts, embryonic and extraembryonic lineages first show different epigenetic marks. This epigenetic reprogramming is likely to be needed for totipotency, correct initiation of embryonic gene expression, and early lineage development in the embryo. Comparative work demonstrates reprogramming in all mammalian species analysed, but the extent and timing varies, consistent with notable differences between species during preimplantation development. Parental imprinting marks originate in sperm and oocytes and are generally protected from this genome-wide reprogramming. Early primordial germ cells possess imprinting marks similar to those of somatic cells. However, rapid DNA demethylation after midgestation erases these parental imprints, in preparation for sex-specific de novo methylation during gametogenesis. Aberrant reprogramming of somatic epigenetic marks after somatic cell nuclear transfer leads to epigenetic defects in cloned embryos and stem cells. Links between epigenetic marking systems appear to be developmentally regulated contributing to plasticity. A number of activities that confer epigenetic marks are firmly established, while for those that remove marks, particularly methylation, some interesting candidates have emerged recently which need thorough testing in vivo. A mechanistic understanding of reprogramming will be crucial for medical applications of stem cell technology.", 
"Background: In animal models, variations in early maternal care are associated with differences in hypothalamic-pituitary-adrenal (HPA) stress response in the offspring, mediated via changes in the epigenetic regulation of glucocorticoid receptor (GR) gene (Nr3c1) expression. Objective: To study this in humans, relationships between prenatal exposure to maternal mood and the methylation status of a CpG-rich region in the promoter and exon 1F of the human GR gene (NR3C1) in newborns and HPA stress reactivity at age three months were examined. Results: Prenatal exposure to increased third trimester maternal depressed/anxious mood was associated with increased methylation of NR3C1 at a predicted NGFI-A binding site. Increased NR3C1 methylation at this site was also associated with increased salivary cortisol stress responses at 3 months, controlling for prenatal SRI exposure, postnatal age and pre and postnatal maternal mood. Methods: The methylation status of a CpG-rich region of the NR3C1 gene, including exon 1F, in genomic DNA from cord blood mononuclear cells was quantified by bisulfite pyrosequencing in infants of depressed mothers treated with a serotonin reuptake inhibitor antidepressant (SRI) (n = 33), infants of depressed non treated mothers (n = 13) and infants of non depressed/non treated mothers (n = 36). To study the functional implications of the newborn methylation status of NR3C1 in newborns, HPA function was assessed at three months using salivary cortisol obtained before and following a non noxious stressor and at a late afternoon basal time. Conclusions: Methylation status of the human NR3C1 gene in newborns is sensitive to prenatal maternal mood and may offer a potential epigenetic process that links antenatal maternal mood and altered HPA stress reactivity during infancy.", 
"The formation of heterochromatin, which requires methylation of histone H3 at lysine 9 and the subsequent recruitment of chromodomain proteins such as heterochromatin protein HP1, serves as a model for the role of histone modifications and chromatin assembly in epigenetic control of the genome. Recent studies in Schizosaccharomyces pombe indicate that heterochromatin serves as a dynamic platform to recruit and spread a myriad of regulatory proteins across extended domains to control various chromosomal processes, including transcription, chromosome segregation and long-range chromatin interactions.", 
"Compelling evidence suggests that the transcription factor Foxp3 acts as a master switch governing the development and function of CD4(+) regulatory T cells (Tregs). However, whether transcriptional control of Foxp3 expression itself contributes to the development of a stable Treg lineage has thus far not been investigated. We here identified an evolutionarily conserved region within the foxp3 locus upstream of exon-1 possessing transcriptional activity. Bisulphite sequencing and chromatin immunoprecipitation revealed complete demethylation of CpG motifs as well as histone modifications within the conserved region in ex vivo isolated Foxp3(+)CD25(+)CD4(+) Tregs, but not in naive CD25(-) CD4(+) T cells. Partial DNA demethylation is already found within developing Foxp3(+) thymocytes; however, Tregs induced by TGF-beta in vitro display only incomplete demethylation despite high Foxp3 expression. In contrast to natural Tregs, these TGF-beta-induced Foxp3(+) Tregs lose both Foxp3 expression and suppressive activity upon restimulation in the absence of TGF-beta. Our data suggest that expression of Foxp3 must be stabilized by epigenetic modification to allow the development of a permanent suppressor cell lineage, a finding of significant importance for therapeutic applications involving induction or transfer of Tregs and for the understanding of long-term cell lineage decisions.", 
"Many genes associated with CpG islands undergo de novo methylation in cancer. Studies have suggested that the pattern of this modification may be partially determined by an instructive mechanism that recognizes specifically marked regions of the genome(1). Using chromatin immunoprecipitation analysis, here we show that genes methylated in cancer cells are specifically packaged with nucleosomes containing histone H3 trimethylated on Lys27. This chromatin mark is established on these unmethylated CpG island genes early in development and then maintained in differentiated cell types by the presence of an EZH2- containing Polycomb complex(2,3). In cancer cells(4), as opposed to normal cells, the presence of this complex brings about the recruitment of DNA methyl transferases, leading to de novo methylation. These results suggest that tumor-specific targeting of de novo methylation is pre-programmed by an established epigenetic system that normally has a role in marking embryonic genes for repression(2).", 
"Ageing results from complex genetically and epigenetically programmed processes that are elicited in part by noxious or stressful events that cause programmed cell death. Here, we report that administration of spermidine, a natural polyamine whose intracellular concentration declines during human ageing, markedly extended the lifespan of yeast, flies and worms, and human immune cells. In addition, spermidine administration potently inhibited oxidative stress in ageing mice. In ageing yeast, spermidine treatment triggered epigenetic deacetylation of histone H3 through inhibition of histone acetyltransferases (HAT), suppressing oxidative stress and necrosis. Conversely, depletion of endogenous polyamines led to hyperacetylation, generation of reactive oxygen species, early necrotic death and decreased lifespan. The altered acetylation status of the chromatin led to significant upregulation of various autophagy-related transcripts, triggering autophagy in yeast, flies, worms and human cells. Finally, we found that enhanced autophagy is crucial for polyamine-induced suppression of necrosis and enhanced longevity.", 
"Induced pluripotent stem (iPS) cells are derived by epigenetic reprogramming, but their DNA methylation patterns have not yet been analyzed on a genome-wide scale. Here, we find substantial hypermethylation and hypomethylation of cytosine-phosphate-guanine (CpG) island shores in nine human iPS cell lines as compared to their parental fibroblasts. The differentially methylated regions (DMRs) in the reprogrammed cells (denoted R-DMRs) were significantly enriched in tissue-specific (T-DMRs; 2.6-fold, P < 10(-4)) and cancer-specific DMRs (C-DMRs; 3.6-fold, P < 10(-4)). Notably, even though the iPS cells are derived from fibroblasts, their R-DMRs can distinguish between normal brain, liver and spleen cells and between colon cancer and normal colon cells. Thus, many DMRs are broadly involved in tissue differentiation, epigenetic reprogramming and cancer. We observed colocalization of hypomethylated R-DMRs with hypermethylated C-DMRs and bivalent chromatin marks, and colocalization of hypermethylated R-DMRs with hypomethylated C-DMRs and the absence of bivalent marks, suggesting two mechanisms for epigenetic reprogramming in iPS cells and cancer.", 
"Histone methylation has important roles in regulating gene expression and forms part of the epigenetic memory system that regulates cell fate and identity. Enzymes that directly remove methyl marks from histones have recently been identified, revealing a new level of plasticity within this epigenetic modification system. Here we analyse the evolutionary relationship between Jumonji C ( JmjC)-domain-containing proteins and discuss their cellular functions in relation to their potential enzymatic activities.", 
"Protein lysine deacetylases have a pivotal role in numerous biological processes and can be divided into the Rpd3/Hda1 and sirtuin families, each having members in diverse organisms including prokaryotes. In vertebrates, the Rpd3/Hda1 family contains 11 members, traditionally referred to as histone deacetylases (HDAC)1-11, which are further grouped into classes I, II and IV. Whereas most class I HDACs are subunits of multiprotein nuclear complexes that are crucial for transcriptional repression and epigenetic landscaping, class II members regulate cytoplasmic processes or function as signal transducers that shuttle between the cytoplasm and the nucleus. Little is known about class IV HDAC11, although its evolutionary conservation implies a fundamental role in various organisms.", 
"Recent investigations have implicated long antisense noncoding RNAs in the epigenetic regulation of chromosomal domains. Here we show that Kcnq1ot1 is an RNA polymerase II-encoded, 91 kb-long, moderately stable nuclear transcript and that its stability is important for bidirectional silencing of genes in the Kcnq1 domain. Kcnq1ot1 interacts with chromatin and with the H3K9- and H3K27-specific histone methyltransferases G9a and the PRC2 complex in a lineage-specific manner. This interaction correlates with the presence of extended regions of chromatin enriched with H3K9me3 and H3K27me3 in the Kcnq1 domain in placenta, whereas fetal liver lacks both chromatin interactions and heterochromatin structures. In addition, the Kcnq1 domain is more often found in contact with the nucleolar compartment in placenta than in liver. Taken together, our data describe a mechanism whereby Kcnq1ot1 establishes lineage-specific transcriptional silencing patterns through recruitment of chromatin remodeling complexes and maintenance of these patterns through subsequent cell divisions occurs via targeting the associated regions to the perinucleolar compartment.", 
"It is more evident now than ever that nucleosomes can transmit epigenetic information from one cell generation to the next. It has been demonstrated during the past decade that the post-translational modifications of histone proteins within the chromosome impact chromatin structure, gene transcription, and epigenetic information. Multiple modifications decorate each histone tail within the nucleosome, including some amino acids that can be modified in several different ways. Covalent modifications of histone tails known thus far include acetylation, phosphorylation, surnoylation, ubiquitination, and methylation. A large body of experimental evidence compiled during the past several years has demonstrated the impact of histone acetylation on transcriptional control. Although histone modification by methylation and ubiquitination was discovered long ago, it was only recently that functional roles for these modifications in transcriptional regulation began to surface. Highlighted in this review are the recent biochemical, molecular, cellular, and physiological functions of histone methylation and ubiquitination involved in the regulation of gene expression as determined by a combination of enzymological, structural, and genetic methodologies.", 
"Cells employ elaborate mechanisms to introduce structural and chemical variation into chromatin. Here, we focus on one such element of variation: methylation of lysine 4 in histone H3 (H3K4). We assess a growing body of literature, including treatment of how the mark is established, the patterns of methylation, and the functional consequences of this epigenetic signature. We discuss structural aspects of the H3K4 methyl recognition by the downstream effectors and propose a distinction between sequence-specific recruitment mechanisms and stabilization on chromatin through methyllysine recognition. Finally, we hypothesize how the unique properties of the polyvalent chromatin fiber and associated effectors may amplify small differences in methyl-lysine recognition, simultaneously allowing for a dynamic chromatin architecture.", 
"Embryonic stem cells rely on Polycomb group proteins to reversibly repress genes required for differentiation. We report that stem cell Polycomb group targets are up to 12-fold more likely to have cancer- specific promoter DNA hypermethylation than non-targets, supporting a stem cell origin of cancer in which reversible gene repression is replaced by permanent silencing, locking the cell into a perpetual state of self-renewal and thereby predisposing to subsequent malignant transformation.", 
"Adult cancers may derive from stem or early progenitor cells(1,2). Epigenetic modulation of gene expression is essential for normal function of these early cells but is highly abnormal in cancers, which often show aberrant promoter CpG island hypermethylation and transcriptional silencing of tumor suppressor genes and pro-differentiation factors(3-5). We find that for such genes, both normal and malignant embryonic cells generally lack the hypermethylation of DNA found in adult cancers. In embryonic stem cells, these genes are held in a 'transcription- ready' state mediated by a 'bivalent' promoter chromatin pattern consisting of the repressive mark, histone H3 methylated at Lys27 ( H3K27) by Polycomb group proteins, plus the active mark, methylated H3K4. However, embryonic carcinoma cells add two key repressive marks, dimethylated H3K9 and trimethylated H3K9, both associated with DNA hypermethylation in adult cancers(6-8). We hypothesize that cell chromatin patterns and transient silencing of these important regulatory genes in stem or progenitor cells may leave these genes vulnerable to aberrant DNA hypermethylation and heritable gene silencing during tumor initiation and progression.", 
" ", 
"Patterns of DNA methylation and chromatin structure are profoundly altered in neoplasia and include genome-wide losses of, and regional gains in, DNA methylation. The recent explosion in our knowledge of how chromatin organization modulates gene transcription has further highlighted the importance of epigenetic mechanisms in the initiation and progression of human cancer. These epigenetic changes - in particular, aberrant promoter hypermethylation that is associated with inappropriate gene silencing - affect virtually every step in tumour progression. In this review, we discuss these epigenetic events and the molecular alterations that might cause them and/or underlie altered gene expression in cancer.", 
"Cells of a multicellular organism are genetically homogeneous but structurally and functionally heterogeneous owing to the differential expression of genes. Many of these differences in gene expression arise during development and are subsequently retained through mitosis. Stable alterations of this kind are said to be 'epigenetic', because they are heritable in the short term but do not involve mutations of the DNA itself. Research over the past few years has focused on two molecular mechanisms that mediate epigenetic phenomena: DNA methylation and histone modifications. Here, we review advances in the understanding of the mechanism and role of DNA methylation in biological processes. Epigenetic effects by means of DNA methylation have an important role in development but can also arise stochastically as animals age. Identification of proteins that mediate these effects has provided insight into this complex process and diseases that occur when it is perturbed. External influences on epigenetic processes are seen in the effects of diet on long-term diseases such as cancer. Thus, epigenetic mechanisms seem to allow an organism to respond to the environment through changes in gene expression. The extent to which environmental effects can provoke epigenetic responses represents an exciting area of future research.", 
"Epithelial and hematopoietic cells have a high turnover and their progenitor cells divide continuously, making them prime targets for genetic and epigenetic changes that lead to cell transformation and tumorigenesis. The consequent changes in cell behavior and responsiveness result not only from genetic alterations such as activation of oncogenes or inactivation of tumor suppressor genes, but also from altered production of, or responsiveness to, stimulatory or inhibitory growth and differentiation factors. Among these, transforming growth factor beta (TGF-beta) and its signaling effectors act as key determinants of carcinoma cell behavior. The autocrine and paracrine effects of TGF-beta on tumor cells and the tumor micro-environment exert both positive and negative influences on cancer development. Accordingly, the TGF-beta signaling pathway has been considered as both a tumor suppressor pathway and a promoter of tumor progression and invasion. Here we evaluate the role of TGF-beta in tumor development and attempt to reconcile the positive and negative effects of TGF-beta in carcinogenesis.", 
"Genomic imprinting affects several dozen mammalian genes and results in the expression of those genes from only one of the two parental chromosomes. This is brought about by epigenetic instructions - imprints - that are laid down in the parental germ cells. Imprinting is a particularly important genetic mechanism in mammals, and is thought to influence the transfer of nutrients to the fetus and the newborn from the mother. Consistent with this view is the fact that imprinted genes tend to affect growth in the womb and behaviour after birth. Aberrant imprinting disturbs development and is the cause of various disease syndromes. The study of imprinting also provides new insights into epigenetic gene modification during development.", 
"The developmental programme of embryogenesis is controlled by both genetic and epigenetic mechanisms. An emerging theme from recent studies is that the regulation of higher-order chromatin structures by DNA methylation and histone modification is crucial for genome reprogramming during early embryogenesis and gametogenesis, and for tissue-specific gene expression and global gene silencing. Disruptions to chromatin modification can lead to the dysregulation of developmental processes, such as X-chromosome inactivation and genomic imprinting, and to various diseases. Understanding the process of epigenetic reprogramming in development is important for studies of cloning and the clinical application of stem-cell therapy.", 
"Early nutrition affects adult metabolism in humans and other mammals, potentially via persistent alterations in DNA methylation. With viable yellow agouti (A(vy)) mice, which harbor a transposable element in the agouti gene, we tested the hypothesis that the metastable methylation status of specific transposable element insertion sites renders them epigenetically labile to early methyl donor nutrition. Our results show that dietary methyl supplementation of ala dams with extra folic acid, vitamin B-12, choline, and betaine alter the phenotype of their A(vy)/a offspring via increased CpG methylation at the A(vy) locus and that the epigenetic metastability which confers this lability is due to the A(vy) transposable element. These findings suggest that dietary supplementation, long presumed to be purely beneficial, may have unintended deleterious influences on the establishment of epigenetic gene regulation in humans.", 
"Recently, the concept that epigenetic, as well as genetic, events might be central to the evolution of human cancer is re-emerging. Cancers often exhibit an aberrant methylation of gene promoter regions that is associated with loss of gene function. This DNA change constitutes a heritable state, not mediated by altered nucleotide sequence, that appears to be tightly linked to the formation of transcriptionally repressive chromatin. This epigenetic process acts as an alternative to mutations to disrupt tumor-suppressor gene function and can predispose to genetic alterations through inactivating DNA-repair genes. Dissecting the molecular processes that mediate these methylation changes will enhance our understanding of chromatin modeling and gene regulation and might present novel possibilities for cancer therapy. Methylation changes constitute potentially sensitive molecular markers to define risk states, monitor prevention strategies, achieve early diagnosis, and track the prognosis of cancer.", 
"Polyploidy is a prominent process in plants and has been significant in the evolutionary history of vertebrates and other eukaryotes. In plants, interdisciplinary approaches combining phylogenetic and molecular genetic perspectives have enhanced our awareness of the myriad genetic interactions made possible by polyploidy. Here, processes and mechanisms of gene and genome evolution in polyploids are reviewed. Genes duplicated by polyploidy may retain their original or similar function, undergo diversification in protein function or regulation, or one copy may become silenced through mutational or epigenetic means. Duplicated genes also may interact through inter-locus recombination, gene conversion, or concerted evolution. Recent experiments have illuminated important processes in polyploids that operate above the organizational level of duplicated genes. These include inter-genomic chromosomal exchanges, saltational, non-Mendelian genomic evolution in nascent polyploids, inter-genomic invasion, and cytonuclear stabilization. Notwithstanding many recent insights, much remains to be learned about many aspects of polyploid evolution, including: the role of transposable elements in structural and regulatory gene evolution; processes and significance of epigenetic silencing; underlying controls of chromosome pairing; mechanisms and functional significance of rapid genome changes; cytonuclear accommodation; and coordination of regulatory factors contributed by two, sometimes divergent progenitor genomes. Continued application of molecular genetic approaches to questions of polyploid genome evolution holds promise for producing lasting insight into processes by which novel genotypes are generated and ultimately into how polyploidy facilitates evolution and adaptation.", 
"Histone H3 lysine 9 methylation has been proposed to provide a major switch for the functional organization of chromosomal subdomains. Here, we show that the murine Suv39h histone methyltransferases (HMTases) govern H3-K9 methylation at pericentric heterochromatin and induce a specialized histone methylation pattern that differs from the broad H3-K9 methylation present at other chromosomal regions. Suv39h-deficient mice display severely impaired viability and chromosomal instabilities that are associated with an increased tumor risk and perturbed chromosome interactions during male meiosis. These in vivo data assign a crucial role for pericentric H3-K9 methylation in protecting genome stability, and define the: Suv39h HMTases as important epigenetic regulators for mammalian development.", 
"Transcriptional activation of a gene involves an orchestrated recruitment of components of the basal transcription machinery and intermediate factors, concomitant with an alteration in local chromatin structure generated by posttranslational modifications of histone tails and nucleosome remodeling. We provide here a comprehensive picture of events resulting in transcriptional activation of a gene, through evaluating the estrogen receptor-alpha (NR3A1) target pS2 gene promoter in MCF-7 cells. This description integrates chromatin remodeling with a kinetic evaluation of cyclical networks of association of 46 transcription factors with the promoter, as determined by chromatin immunoprecipitation assays. We define the concept of a transcriptional clock that directs and achieves the sequential and combinatorial assembly of a transcriptionally productive complex on a promoter. Furthermore, the unanticipated findings of key roles for histone deacetylases and nucleosome-remodeling complexes in limiting transcription implies that transcriptional activation is a cyclical process that requires both activating and repressive epigenetic processes.", 
"Hepatocarcinogenesis is a slow process during which genomic changes progressively alter the hepatocellular phenotype to produce cellular intermediates that evolve into hepatocellular carcinoma. During the long pre-neoplastic stage, in which the liver is often the site of chronic hepatitis, cirrhosis, or both, hepatocyte cycling is accelerated by upregulation of mitogenic pathways, in part through epigenetic mechanisms. This leads to the production of monoclonal populations of aberrant and dysplastic hepatocytes that have telomere erosion and telomerase re-expression, sometimes microsatellite instability, and occasionally structural aberrations in genes and chromosomes. Development of dysplastic hepatocytes in foci and nodules and emergence of hepatocellular carcinoma are associated with the accumulation of irreversible structural alterations in genes and chromosomes, but the genomic basis of the malignant phenotype is heterogeneous. The malignant hepatocyte phenotype may be produced by the disruption of a number of genes that function in different regulatory pathways, producing several molecular variants of hepatocellular carcinoma. New strategies should enable these variants to be characterized.", 
"Enhancer of Zeste is a Polycomb Group protein essential for the establishment and maintenance of repression of homeotic and other genes. In the early embryo it is found in a complex that includes ESC and is recruited to Polycomb Response Elements. We show that this complex contains a methyltransferase activity that methylates lysine 9 and lysine 27 of histone H3, but the activity is lost when the E(Z) SET domain is mutated. The lysine 9 position is trimethylated and this mark is closely associated with Polycomb binding sites on polytene chromosomes but is also found in centric heterochromatin, chromosome 4, and telomeric sites. Histone H3 methylated in vitro by the E(Z)/ ESC complex binds specifically to Polycomb protein.", 
"Cytosine-5 DNA methylation occurs in the context of CpG dinucleotides in vertebrates. Aberrant methylation of CpG islands in human tumors has been shown to cause transcriptional silencing of tumor-suppressor genes. Most methods used to analyze cytosine-5 methylation patterns require cumbersome manual techniques that employ gel electrophoresis, restriction enzyme digestion, radiolabeled dNTPs or hybridization probes. The development of high-throughput technology for the analysis of DNA methylation would significantly expand our ability to derive molecular information from clinical specimens. This study describes a high-throughput quantitative methylation assay that utilizes fluorescence-based real-time PCR (TaqMan (R)) technology that requires no further manipulations after the PCR step. Methy-Light is a highly sensitive assay, capable of detecting methylated alleles in the presence of a 10 000-fold excess of unmethylated alleles. The assay is also highly quantitative and can very accurately determine the relative prevalence of a particular pattern of DNA methylation. We show that MethyLight can distinguish between mono-allelic and bi-allelic methylation of the MLH1 mismatch repair gene in human colorectal tumor specimens. The development of this technique should considerably enhance our ability to rapidly and accurately generate epigenetic profiles of tumor samples.", 
"Cancer-associated DNA hypomethylation is as prevalent as cancer-linked hypermethylation, but these two types of epigenetic abnormalities usually seem to affect different DNA sequences. Much more of the genome is generally subject to undermethylation rather than overmethylation. Genomic hypermethylation in cancer has been observed most often in CpG islands in gene regions. In contrast, very frequent hypomethylation is seen in both highly and moderately repeated DNA sequences in cancer, including heterochromatic DNA repeats, dispersed retrotransposons, and endogenous retroviral elements. Also, unique sequences, including transcription control sequences, are often subject to cancer-associated undermethylation. The high frequency of cancer-linked DNA hypomethylation, the nature of the affected sequences, and the absence of associations with DNA hypermethylation are consistent with an independent role for DNA undermethylation in cancer formation or tumor progression. Increased karyotypic instability and activation of tumor-promoting genes by cis or trans effects, that might include altered heterochromatin-euchromatin interactions, may be important consequences of DNA hypomethylation which favor oncogenesis. The relationship of DNA hypomethylation to tumorigenesis is important to be considered in the light of cancer therapies involving decreasing DNA methylation. Inducing DNA hypomethylation may have short-term anticancer effects, but might also help speed tumor progression from cancer cells surviving the DNA demethylation chemotherapy.", 
"Sirtuins (Sir2-like proteins) are present in prokaryotes and eukaryotes, Here, two new human sirtuins (SIRT6 and SIRT7) are found to be similar to a particular subset of insect, nematode, plant, and protozoan sirtuins. Molecular phylogenetic analysis of 60 sirtuin conserved core domain sequences from a diverse array of organisms (including archaeans, bacteria, yeasts, plants, protozoans, and metazoans) shows that eukaryotic Sir2-like proteins group into four main branches designated here as classes I-IV. Prokaryotic sirtuins include members of classes II and III. A fifth class of sirtuin is present in gram positive bacteria and Thermotoga maritima. Saccharomyces cerevisiae has five class I sirtuins. Caenorhabditis elegans and Drosophila melanogaster have sirtuin genes from classes I, II, and TV. The seven human sirtuin genes include all four classes: SIRT1, SIRT2, and SIRT3 are class I, SIRT4 is class II, SIRT5 is class III, and SIRT6 and SIRT7 are class IV. (C) 2000 Academic Press.", 
"Chromatin is the physiologically relevant substrate for all genetic processes inside the nuclei of eukaryotic cells. Dynamic changes in the local and global organization of chromatin are emerging as key regulators of genomic function. Indeed, a multitude of signals from outside and inside the cell converges on this gigantic signaling platform. Numerous post-translational modifications of histones, the main protein components of chromatin, have been documented and analyzed in detail. These 'marks' appear to crucially mediate the functional activity of the genome in response to upstream signaling pathways. Different layers of cross-talk between several components of this complex regulatory system are emerging, and these epigenetic circuits are the focus of this review.", 
"Allelic loss at the short arm of chromosome 3 is one of the most common and earliest events in the pathogenesis of lung cancer, and is observed in more than 90% of small-cell lung cancers (SCLCs) and in 50-80% of non-small-cell lung cancers(1,2) (NSCLCs). Frequent and early loss of heterozygosity and the presence of homozygous deletions suggested a critical role of the region 3p21.3 in tumorigenesis(2-4) and a region of common homozygous deletion in 3p21.3 was narrowed to 120 kb (ref. 5). Several putative tumour-suppressor genes located at 3p21 have been characterized, but none of these genes appear to be altered in lung cancer. Here we describe the cloning and characterization of a human RAS effector homologue (RASSF1) located in the 120-kb region of minimal homozygous deletion. We identified three transcripts, A, B and C, derived from alternative splicing and promoter usage. The major transcripts A and C were expressed in all normal tissues. Transcript A was missing in all SCLC cell lines analysed and in several other cancer cell lines. loss of expression was correlated with methylation of the CpG-island promoter sequence of RASSF1A. The promoter was highly methylated in 24 of 60 (40%) primary lung tumours, and 4 of 41 tumours analysed carried missense mutations. Re-expression of transcript A in lung carcinoma cells reduced colony formation, suppressed anchorage-independent growth and inhibited tumour formation in nude mice. These characteristics indicate a potential role for RASSF1A asa lung tumour suppresor gene.", 
"Deposition of the major histone H3 (H3.1) is coupled to DNA synthesis during DNA replication and possibly DNA repair, whereas histone variant H3.3 serves as the replacement variant for the DNA-synthesis-independent deposition pathway. To address how histories H3.1 and H3.3 are deposited into chromatin through distinct pathways, we have purified deposition machineries for these histories. The H3.1 and H3.3 complexes contain distinct histone chaperones, CAF-1 and HIRA, that we show are necessary to mediate DNA-synthesis-dependent and -independent nucleosome assembly, respectively. Notably, these complexes possess one molecule each of H3.1/H3.3 and H4, suggesting that histories H3 and H4 exist as dimeric units that are important intermediates in nucleosome formation. This finding provides new insights into possible mechanisms for maintenance of epigenetic information after chromatin duplication.", 
"Dynamic epigenetic modification of the genome occurs during early development of the mouse. Active demethylation of the paternal genome occurs in the zygote, followed by passive demethylation during cleavage stages, and de novo methylation, which is thought to happen after implantation. We have investigated these processes by using indirect immunofluoresence with an antibody to 5-methyl cytosine. In contrast to previous work, we show that demethylation of the male pronucleus is completed within 4 h of fertilisation. This activity is intricately linked with and not separable from pronucleus formation. In conditions permissive for polyspermy, up to five male pronuclei underwent demethylation in the same oocyte. Paternal demethylation in fertilised oocytes deficient for MBD2, the only candidate demethylase, occurred normally. Passive loss of methylation occurred in a stepwise fashion up to the morulae stage without any evidence of spatial compartmentalisation. De novo methylation was observed specifically in the inner cell mass (ICM) but not in the trophectoderm of the blastocyst and hence may have an important role in early lineage specification. This is the first complete and detailed analysis of the epigenetic reprogramming cycle during preimplantation development. The three phases of methylation reprogramming may have roles in imprinting, the control of gene expression, and the establishment of nuclear totipotency. (C) 2001 Elsevier Science.", 
"5-Azacytidine was first synthesized almost 40 years ago. It was demonstrated to have a wide range of anti-metabolic activities when tested against cultured cancer cells and to be an effective chemotherapeutic agent for acute myelogenous leukemia. However, because of 5-azacytidine's general toxicity, other nucleoside analogs were favored as therapeutics. The finding that 5-azacytidine was incorporated into DNA and that, when present in DNA, it inhibited DNA methylation, led to widespread use of 5-azacytidine and 5-aza-2'-deoxycytidine (Decitabine) to demonstrate the correlation between loss of methylation in specific gene regions and activation of the associated genes. There is now a revived interest in the use of Decitabine as a therapeutic agent for cancers in which epigenetic silencing of critical regulatory genes has occurred. Here, the current status of our understanding of the mechanism(s) by which 5-azacytosine residues in DNA inhibit DNA methylation is reviewed with an emphasis on the interactions of these residues with bacterial and mammalian DNA (cytosine-C5) methyltransferases. The implications of these mechanistic studies for development of less toxic inhibitors of DNA methylation are discussed.", 
"The enzyme-catalyzed acetylation of the N-terminal tail domains of core histones provides a rich potential source of epigenetic information. This may be used both to mediate transient changes in transcription, through modification of promoter-proximal nucleosomes, and for the longer-term maintenance and modulation of patterns of gene expression. The latter may be achieved by setting specific patterns of histone acetylation, perhaps involving acetylation of particular lysine residues, across relatively large chromatin domains. The histone acetylating and deacetylating enzymes (HATs and HDACs, respectively) can be targeted to specific regions of the genome and show varying degrees of substrate specificity, properties that are consistent with a role in maintaining a dynamic, acetylation-based epigenetic code. The code may be read (ie. exert a functional effect) either through non-histone proteins that bind in an acetylation-dependent manner, or through direct effects on chromatin structure. Recent evidence raises the interesting possibility that an acetylation-based code may operate through both mitosis and meiosis, providing a possible mechanism for germ-line transmission of epigenetic changes. BioEssays 22:836-845, 2000. (C) 2000 John Wiley & Sons, Inc.", 
"We have come a long way since the first reports of the existence of aberrant DNA methylation in human cancer. Hypermethylation of CpG islands located in the promoter regions of tumor suppressor genes is now firmly established as an important mechanism for gene inactivation. CpG island hypermethylation has been described in almost every tumor type. Many cellular pathways are inactivated by this type of epigenetic lesion: DNA repair (hMLH1, MGMT), cell cycle (p16(INK4a), p15(INK4b), p14(ARF)), apoptosis (DAPK), cell adherence (CDH1, CDH13), detoxification (GSTP1), etc... However, we still know little of the mechanisms of aberrant methylation and why certain genes are selected over others. Hypermethylation is not an isolated layer of epigenetic control, but is linked to the other pieces of the puzzle such as methyl-binding proteins, DNA methyltransferases and histone deacetylase, but our understanding of the degree of specificity of these epigenetic layers in the silencing of specific tumor suppressor genes remains incomplete. The explosion of user-friendly technologies has given rise to a rapidly increasing list of hypermethylated genes. Careful functional and genetic studies are necessary to determine which hypermethylation events are truly relevant for human tumorigenesis. The development of CpG island hypermethylation profiles for every form of human tumors has yielded valuable pilot clinical data in monitoring and treating cancer patients based in our knowledge of DNA methylation. Basic and translational will both be needed in the near future to fully understand the mechanisms, roles and uses of CpG island hypermethylation in human cancer. The expectations are high.", 
"Genome-wide epigenetic reprogramming in mammalian germ cells, zygote and early embryos, plays a crucial role in regulating genome functions at critical stages of development. We show here that mouse primordial germ cells (PGCs) exhibit dynamic changes in epigenetic modifications between days 10.5 and 12.5 post coitum (dpc). First, contrary to previous suggestions, we show that PGCs do indeed acquire genome-wide de novo methylation during early development and migration into the genital ridge. However, following their entry into the genital ridge, there is rapid erasure of DNA methylation of regions within imprinted and non-imprinted loci. For most genes, the erasure commences simultaneously in PGCs in both male and female embryos, which is completed within I day of development. Based on the kinetics of this process, we suggest that this is an active demethylation process initiated upon the entry of PGCs into the gonadal anlagen. The timing of reprogramming in PGCs is crucial since it ensures that germ cells of both sexes acquire an equivalent epigenetic state prior to the differentiation of the definitive male and female germ cells in which new parental imprints are established subsequently. Some repetitive elements, however, show incomplete erasure, which may be essential for chromosome stability and for preventing activation of transposons to reduce the risk of germline mutations. Aberrant epigenetic reprogramming in the germ line would cause the inheritance of epimutations that may have consequences for human diseases as suggested by studies on mouse models. (C) 2002 Elsevier Science Ireland Ltd. All rights reserved.", 
"Aberrant WNT pathway signaling is an early progression event in 90% of colorectal cancers(1). It occurs through mutations mainly of APC and less often of CTNNB1 (encoding beta-catenin)(1-3) or AXIN2 (encoding axin-2, also known as conductin)(4). These mutations allow ligand-independent WNT signaling that culminates in abnormal accumulation of free beta-catenin in the nucleus(1-3). We previously identified frequent promoter hypermethylation and gene silencing of the genes encoding secreted frizzled-related proteins (SFRPs) in colorectal cancer(5). SFRPs possess a domain similar to one in the WNT-receptor frizzled proteins and can inhibit WNT receptor binding to downregulate pathway signaling during development(6-10). Here we show that restoration of SFRP function in colorectal cancer cells attenuates WNT signaling even in the presence of downstream mutations. We also show that the epigenetic loss of SFRP function occurs early in colorectal cancer progression and may thus provide constitutive WNT signaling that is required to complement downstream mutations in the evolution of colorectal cancer.", 
"Methylation of position-specific lysine residues in histone N termini is a central modification for regulating epigenetic transitions in chromatin. Each methylatable lysine residue can exist in a mono-, di-, or trimethylated state, thereby extending the indexing potential of this particular modification. Here, we examine all possible methylation states for histone H3 lysine 9 (H3-K9) and lysine 27 (H3-K27) in mammalian chromatin. Using highly specific antibodies together with quantitative mass spectrometry, we demonstrate that pericentric heterochromatin is selectively enriched for H3-K27 monomethylation and H3-K9 trimethylation. This heterochromatic methylation profile is dependent on the Suv39h histone methyltransferases (HMTases) but independent of the euchromatic G9a HMTase. In Suv39h double null cells, pericentric heterochromatin is converted to alternative methylation imprints and accumulates H3-K27 trimethylation and H3-K9 monomethylation. Our data underscore the selective presence of distinct histone lysine methylation states in partitioning chromosomal subdomains but also reveal a surprising plasticity in propagating methylation patterns in eukaryotic chromatin.", 
"During the development of multicellular organisms, cells become different from one another by changing their genetic program in response to transient stimuli. Long after the stimulus is gone, cellular memory mechanisms enable cells to remember their chosen fate over many cell divisions. The Polycomb and Trithorax groups of proteins, respectively, work to maintain repressed or active transcription states of developmentally important genes through many rounds of cell division. Here we review current ideas on the protein and DNA components of this transcriptional memory system and how they interact dynamically with each other to orchestrate cellular memory for several hundred genes.", 
"DNA methylation has recently moved to centre stage in the aetiology of human neurodevelopmental syndromes such as the fragile X, ICF and Rett syndromes. These diseases result from the misregulation of genes that occurs with the toss of appropriate epigenetic controls during neuronal development. Recent advances have connected DNA methylation to chromatin-remodeling enzymes, and understanding this link will be central to the design of new therapeutic tools.", 
"The centromere is a chromosomal locus that ensures delivery of one copy of each chromosome to each daughter at cell division. Efforts to understand the nature and specification of the centromere have demonstrated that this central element for ensuring inheritance is itself epigenetically determined. The kinetochore, the protein complex assembled at each centromere, serves as the attachment site for spindle microtubules and the site at which motors generate forces to power chromosome movement. Unattached kinetochores are also the signal generators for the mitotic checkpoint, which arrests mitosis until all kinetochores have correctly attached to spindle microtubules, thereby representing the major cell cycle control mechanism protecting against loss of a chromosome (aneuploidy).", 
"On the histone H3 tail, Lys 9 and Lys 27 are both methylation sites associated with epigenetic repression, and reside within a highly related sequence motif ARKS. Here we show that the chromodomain proteins Polycomb (Pc) and HP1 (heterochromatin protein 1) are highly discriminatory for binding to these sites in vivo and in vitro. In Drosophila S2 cells, and on polytene chromosomes, methyl-Lys 27 and Pc are both excluded from areas that are enriched in methyl-Lys 9 and HP1. Swapping of the chromodomain regions of Pc and HP1 is sufficient for switching the nuclear localization patterns of these factors, indicating a role for their chromodomains in both target site binding and discrimination. To better understand the molecular basis for the selection of methyl-lysine binding sites, we solved the 1.8 Angstrom structure of the Pc chromodomain in complex with a H3 peptide bearing trimethyl-Lys 27, and compared it with our previously determined structure of the HP1 chromodomain in complex with a H3 peptide bearing trimethyl-Lys 9. The Pc chromodomain distinguishes its methylation target on the H3 tail via an extended recognition groove that binds five additional residues preceding the ARKS motif.", 
"DNA methylation is essential for the control of a number of biological mechanisms in mammals [1]. Mammalian development is accompanied by two major waves of genome-wide demethylation and remethylation: one during germ-cell development and the other after fertilisation [2-7]. Most previous studies have suggested that the genome-wide demethylation observed after fertilisation occurs passively, that is, by the lack of maintenance methylation following DNA replication and cell division [6,7], although one other study has reported that replication-independent demethylation may also occur during early embryogenesis [8]. Here, we report that genes that are highly methylated in sperm are rapidly demethylated in the zygote only hours after fertilisation, before the first round of DNA replication commences. By contrast, the oocyte-derived maternal alleles are unaffected by this reprogramming. They either remain methylated after fertilisation or become further methylated de novo. These results provide the first direct evidence for active demethylation of single-copy genes in the mammalian zygote and, moreover, reveal a striking asymmetry in epigenetic methylation reprogramming. Whereas paternally (sperm)-derived sequences are exposed to putative active demethylases in the oocyte cytoplasm, maternally (oocyte)-derived sequences are protected from this reaction. These results, whose generality is supported by findings of Mayer et al. [9], have important implications for the establishment of biparental genetic totipotency after fertilisation, the establishment and maintenance of genomic imprinting, and the reprogramming of somatic cells during cloning.", 
"Aberrant hypermethylation of gene promoters is a major mechanism associated with inactivation of tumor-suppressor genes in cancer. We previously showed this transcriptional silencing to be mediated by both methylation and histone deacetylase activity, with methylation being dominant. Here, we have used cDNA microarray analysis to screen for genes that are epigenetically silenced in human colorectal cancer. By screening over 10,000 genes, we show that our approach can identify a substantial number of genes with promoter hypermethylation in a given cancer; these are distinct from genes with unmethylated promoters, for which increased expression is produced by histone deacetylase inhibition alone. Many of the hypermethylated genes we identified have high potential for roles in tumorigenesis by virtue of their predicted function and chromosome position. We also identified a group of genes that are preferentially hypermethylated in colorectal cancer and gastric cancer. One of these genes, SFRP1, belongs to a gene family; we show that hypermethylation of four genes in this family occurs very frequently in colorectal cancer, providing for (i) a unique potential mechanism for loss of tumor-suppressor gene function and (ii) construction of a molecular marker panel that could detect virtually all colorectal cancer.", 
"Gene function in cancer can be disrupted either through genetic alterations, which directly mutate or delete genes, or epigenetic alterations, which alter the heritable state of gene expression. The latter events are mediated by formation of transcriptionally repressive chromatin states around gene transcription start sites and an associated gain of methylation in normally unmethylated CpG islands in these regions. The genes affected include over half of the tumor suppressor genes that cause familial cancers when mutated in the germline; the selective advantage for genetic and epigenetic dysfunction in these genes is very similar. The aberrant methylation can begin very early in tumor progression and mediate most of the important pathway abnormalities in cancer including loss of cell cycle control, altered function of transcription factors, altered receptor function, disruption of normal cell-cell and cell-substratum interaction, inactivation of signal transduction pathways, loss of apoptotic signals and genetic instability. The active role of the aberrant methylation in transcriptional silencing of genes is becoming increasingly understood and involves a synergy between the methylation and histone deacetylase (HDAC) activity, This synergy can be mediated directly by HDAC interaction with DNA methylating enzymes and by recruitment through complexes involving methyl-cytosine binding proteins. In the translational arena, the promoter hypermethylation changes hold great promise as DNA tumor markers and their potentially reversible state creates a target for cancer therapeutic strategies involving gene reactivation.", 
"DNA methylation plays an important role in mammalian development and correlates with chromatin-associated gene silencing. The recruitment of MeCP2 to methylated CpG dinucleotides represents a major mechanism by which DNA methylation can repress transcription. MeCP2 silences gene expression partly by recruiting histone deacetylase (HDAC) activity, resulting in chromatin remodeling. Here, we show that MeCP2 associates with histone methyltransferase activity in vivo and that this activity is directed against Lys(9) of histone H3. Two characterized repression domains of MeCP2 are involved in tethering the histone methyltransferase to MeCP2. We asked if MeCP2 can deliver Lys(9)H3 methylation to the H19 gene, whose activity it represses. We show that the presence of MeCP2 on nucleosomes within the repressor region of the H19 gene (the differentially methylated domain) coincides with an increase in H3 Lys(9) methylation. Our data provide evidence that MeCP2 reinforces a repressive chromatin state by acting as a bridge between two global epigenetic modifications, DNA methylation and histone methylation.", 
"A large set of endogenous small RNAs of predominantly 21 to 24 nucleotides was identified in Arabidopsis. These small RNAs resembled micro-RNAs from animals and were similar in size to small interfering RNAs; that accumulated during RNA silencing triggered by multiple types of inducers. Among the 125 sequences identified, the vast majority (90%) arose from intergenic regions, although small RNAs corresponding to predicted protein-coding genes, transposon-like sequences, and a structural RNA gene also were identified. Evidence consistent with the derivation of small RNAs of both polarities, and from highly base-paired precursors, was obtained through the identification and analysis of clusters of small RNA loci. The accumulation of specific small RNAs was regulated developmentally. We propose that Arabidopsis small RNAs; participate in a wide range of post-transcriptional and epigenetic events.", 
"Recent results from diverse organisms point to a self-reinforcing network of interactions among the three best-characterized covalent modifications that mark heterochromatin: histone hypoacetylation, histone H3-Lys9 methylation, and cytosine methylation. These modification systems suggest a mechanistic basis for spreading of heterochromatin over large domains and for stable epigenetic inheritance of the silent state. All three modifications used in packaging heterochromatin are also used in stable silencing of euchromatic genes.", 
"Recent data in humans and animals suggest that assisted reproductive technology (ART) might affect the epigenetics of early embryogenesis and might cause birth defects. We report the first evidence, to our knowledge, that ART is associated with a human overgrowth syndrome-namely, Beckwith-Wiedemann syndrome (BWS). In a prospective study, the prevalence of ART was 4.6% (3 of 65), versus the background rate of 0.8% in the United States. A total of seven children with BWS were born after ART-five of whom were conceived after intracytoplasmic sperm injection. Molecular studies of six of the children indicate that five of the six have specific epigenetic alterations associated with BWS-four at LIT1 and one at both LIT1 and H19. We discuss the implications of our finding that ART is associated with human overgrowth, similar to the large offspring syndrome reported in ruminants.", 
"Cadmium is a heavy metal of considerable environmental and occupational concern. Cadmium compounds are classified as human carcinogens by several regulatory agencies. The most convincing data that cadmium is carcinogenic in humans comes from studies indicating occupational cadmium exposure is associated with lung cancer. Cadmium exposure has also been linked to human prostate and renal cancer, although this linkage is weaker than for lung cancer. Other target sites of cadmium carcinogenesis in humans, such as liver, pancreas and stomach, are considered equivocal. In animals, cadmium effectively induces cancers at multiple sites and by various routes. Cadmium inhalation in rats induces pulmonary adenocarcinomas, in accord with its role in human lung cancer. Cadmium can induce tumors and/or preneoplastic lesions within the rat prostate after ingestion or injection. At relatively high doses, cadmium induces benign testicular tumors in rats, but these appear to be due to early toxic lesions and loss of testicular function, rather than from a specific carcinogenic effect of cadmium. Like many other metals, cadmium salts will induce mesenchymal tumors at the site of subcutaneous (s.c.) or intramuscular (i.m.) injections, but the human relevance of these is dubious. Other targets of cadmium in rodents include the liver, adrenal, pancreas, pituitary, and hematopoietic system. With the exception of testicular tumors in rodents, the mechanisms of cadmium carcinogenesis are poorly defined. Cadmium can cause any number of molecular lesions that would be relevant to oncogenesis in various cellular model systems. Most studies indicate cadmium is poorly mutagenic and probably acts through indirect or epigenetic mechanisms, potentially including aberrant activation of oncogenes and suppression of apoptosis. (C) 2003 Elsevier B.V. All rights reserved.", 
"Diverse post-translational modifications of histone amino termini represent an important epigenetic mechanism for the organisation of chromatin structure and the regulation of gene activity. Within the past two years, great progress has been made in understanding the functional implications of histone methylation; in particular through the characterisation of histone methyltransferases that direct the site-specific methylation of, for example, lysine 9 and lysine 4 positions in the histone H3 amino terminus. All known histone methyltransferases of this type contain the evolutionarily conserved SET domain and appear to be able to stimulate either gene repression or gene activation. Methylation of H3 Lys9 and Lys4 has been visualised in native chromatin, indicating opposite roles in structuring repressive or accessible chromatin domains. For example, at the mating-type loci in Schizosaccharomyces pombe, at pericentric heterochromatin and at the inactive X chromosome in mammals, striking differences between these distinct marks have been observed. H3 Lys9 methylation is also important to direct additional epigenetic signals such as DNA methylation - for example, in Neurospora crassa and in Arabidopsis thaliana. Together, the available data strongly establish histone lysine methylation as a central modification for the epigenetic organisation of eukaryotic genomes.", 
"Polyploidy has long been recognized as a prominent force shaping the evolution of eukaryotes, especially flowering plants. New phenotypes often arise with polyploid formation and can contribute to the success of polyploids in nature or their selection for use in agriculture. Although the causes of novel variation in polyploids are not well understood, they could involve changes in gene expression through increased variation in dosage-regulated gene expression, altered regulatory interactions, and rapid genetic and epigenetic changes. New research approaches are being used to study these mechanisms and the results should provide a more complete understanding of polyploidy.", 
"Adult germline stem cells are capable of self-renewal, tissue regeneration and production of large numbers of differentiated progeny. We show here that the classical mouse mutant luxoid affects adult germline stem cell self-renewal. Young homozygous luxoid mutant mice produce limited numbers of normal spermatozoa and then progressively lose their germ line after birth. Transplantation studies showed that germ cells from mutant mice did not colonize recipient testes, suggesting that the defect is intrinsic to the stem cells. We determined that the luxoid mutant contains a nonsense mutation in the gene encoding Plzf, a transcriptional repressor that regulates the epigenetic state of undifferentiated cells, and showed that Plzf is coexpressed with Oct4 in undifferentiated spermatogonia. This is the first gene shown to be required in germ cells for stem cell self-renewal in mammals.", 
"The covalent modification of nucleosomal histones has emerged as a major determinant of chromatin structure and gene activity. To understand the interplay between various histone modifications, including acetylation and methylation, we performed a genome-wide chromatin structure analysis in a higher eukaryote. We found a binary pattern of histone modifications among euchromatic genes, with active genes being hyperacetylated for H3 and H4 and hypermethylated at Lys 4 and Lys 79 of 113, and inactive genes being hypomethylated and deacetylated at the same residues. Furthermore, the degree of modification correlates with the level of transcription, and modifications are largely restricted to transcribed regions, suggesting that their regulation is tightly linked to polymerase activity.", 
"Manipulation or non-physiological embryo culture environments can lead to defective fetal programming in livestock. Our demonstration of reduced fetal methylation and expression of ovine IGF2R suggests pre-implantation embryo procedures may be vulnerable to epigenetic alterations in imprinted genes. This highlights the potential benefits of epigenetic diagnostic screening in developing embryo procedures.", 
"Proteins from the Polycomb group (PcG) are epigenetic chromatin modifiers involved in cancer development and also in the maintenance of embryonic and adult stem cells, The therapeutic potential of stem cells and the growing conviction that tumors contain stem cells highlights the importance of understanding the extrinsic and intrinsic circuitry controlling stem cell fate and their connections to cancer.", 
"Genomes are organized into active regions known as euchromatin and inactive regions known as heterochromatin, or silenced chromatin. This review describes contemporary knowledge and models for how silenced chromatin in Saccharomyces cerevisiae forms, functions, and is inherited. In S. cerevisiae, Sir proteins are the key structural components of silenced chromatin. Sir proteins interact first with silencers, which dictate which regions are silenced, and then with histone tails in nucleosomes as the Sir proteins spread from silencers along chromosomes. Importantly, the spreading of silenced chromatin requires the histone deacetylase activity of Sir2p. This requirement leads to a general model for the spreading and inheritance of silenced chromatin or other special chromatin states Such chromatin domains are marked by modifications of the nucleosomes or DNA, and this mark is able to recruit an enzyme that makes further marks. Thus, among different organisms, multiple forms of repressive chromatin can be formed using similar strategies but completely different proteins. We also describe emerging evidence that mutations that cause global changes in the modification of histones can alter the balance between euchromatin and silenced chromatin within a cell.", 
"T lymphocytes differentiate in discrete stages within the thymus. Immature thymocytes lacking CD4 and CD8 coreceptors differentiate into double-positive cells (CD4(+)CD8(+)), which are selected to become either CD4(+)CD8(-)helper cells or CD4(-)CD8(+) cytotoxic cells. A stage-specific transcriptional silencer regulates expression of CD4 in both immature and CD4(-)CD8(+) thymocytes. We show here that binding sites for Runt domain transcription factors are essential for CD4 silencer function at both stages, and that different Runx family members are required to fulfill unique functions at each stage. Runxi is required for active repression in CD4(-)CD8(-) thymocytes whereas Runx3 is required for establishing epigenetic silencing in cytotoxic lineage thymocytes. Runx3-deficient cytotoxic T cells, but not helper cells, have defective responses to antigen, suggesting that Runx proteins have critical functions in lineage specification and homeostasis of CD8lineage T lymphocytes.", 
"The Cyclin D-Cdk4,6/lNK4/Rb/E2F pathway plays a key role in controlling cell growth by integrating multiple mitogenic and antimitogenic stimuli. The components of this pathway are gene families with a high level of structural and functional redundancy and are expressed in an overlapping fashion in most tissues and cell types. Using classical transgenic technology as well as gene-targeting in ES cells, a series of mouse models have been developed to study the in vivo function of individual components of this pathway in both normal homeostasis and tumor development. These models have proven to be useful to define specific as well as redundant roles among members of these cell cycle regulatory gene families. This pathway is deregulated in the vast majority of human tumors by genetic and epigenetic alterations that target at least some of its key members such as Cyclin D1, Cdk4, INK4a and INK4b, pRb etc. As a consequence, some of these molecules are currently being considered as targets for cancer therapy, and several novel molecules, such as Cdk inhibitors, are under development as potential anti-cancer drugs. (C) 2002 Elsevier Science B.V. All rights reserved.", 
"Twin studies have been vital for establishing an important genetic contribution to the etiology of schizophrenia. The five newest studies since 1995 from Europe and Japan have confirmed earlier findings. They yielded probandwise concordance rates of 41-65% in monozygotic (MZ) pairs and 0-28% in dizygotic (DZ) pairs, and heritability estimates of approximately 80-85%. Twin studies are also Valuable for investigating the etiological relationships between schizophrenia and other disorders, and the genetic basis of clinical heterogeneity within schizophrenia. Studies of discordant MZ pairs provide further insights into noninherited factors that contribute to the multifactorial etiology of this disorder. More recently, twin studies have begun to be used to directly investigate molecular genetic and epigenetic processes underlying schizophrenia. (C) 2000 Wiley-Liss, Inc.", 
"Interspecific or intergeneric hybridization, followed by chromosome doubling, can lead to the formation of new allopolyploid species. Recent studies indicate that allopolyploid formation is associated with genetic and epigenetic changes, although little is known about the type of changes that occur, how rapidly they occur, and the type of sequences involved. To address these matters, we have surveyed F1 hybrids between diploid species from the wheat (Aegilops and Triticum) group and their derived allotetraploids by screening a large number of loci using amplified fragment length polymorphism and DNA gel blot analysis and by assaying the extent of cytosine methylation. We found that sequence elimination is one of the major and immediate responses of the wheat genome to wide hybridization or allopolyploidy, that it affects a large fraction of the genome, and that it is reproducible. In one cross between Ae. sharonensis x Ae. umbellulata, 14% of the loci from Ae. sharonensis were eliminated compared with only 0.5% from Ae. umbellulata, with most changes occurring in the F1 hybrid. In contrast, crosses between Ae. longissima x T. urartu showed that sequence elimination was more frequent after chromosome doubling. Alterations in cytosine methylation occurred in similar to 13% of the loci, either in the F1 hybrid or in the allopolyploid. For eight of nine bands that were isolated, the sequences that underwent elimination corresponded to low-copy DNA, whereas alterations in methylation patterns affected both repetitive DNA sequences, such as retrotransposons, and low-copy DNA in approximately equal proportions.", 
"Cytosine methylation in CpG dinucleotides is believed to be important in gene regulation, and is generally associated with reduced levels of transcription. Methylation-mediated gene silencing involves a series of DNA-protein and protein-protein interactions that begins with the binding of methyl-CpG binding proteins (MBPs) followed by the recruitment of histone-modifying enzymes that together promote chromatin condensation and inactivation. It is widely known that alterations in methylation patterns, and associated gene activities, are often found in human tumors. However, the mechanisms by which methylation patterns are altered are not currently understood. In this paper, we investigate the impact of oxidative damage to a methyl-CpG site on MBP binding by the selective placement of 8-oxoguanine (8-oxoG) and 5-hydroxymethylcytosine (HmC) in a MBP recognition sequence. Duplexes containing these specific modifications were assayed for binding to the methyl-CpG binding domain (MBD) of one member of the MBP family, methyl-CpG binding protein 2 (MeCP2). Our results reveal that oxidation of either a single guanine to 8-oxoG or of a single 5mC to HmC, significantly inhibits binding of the MBD to the oligonucleotide duplex, reducing the binding affinity by at least an order of magnitude. Oxidative damage to DNA could therefore result in heritable, epigenetic changes in chromatin organization.", 
"Rett syndrome(1) (RTT, MIM 312750) is a progressive neurodevelopmental disorder and one of the most common causes of mental retardation in females, with an incidence of 1 in 10,000-15,000 (ref. 2). Patients with classic RTT appear to develop normally until 6-18 months of age, then gradually lose speech and purposeful hand use, and develop microcephaly, seizures, autism, ataxia, intermittent hyperventilation and stereotypic hand movements(3). After initial regression, the condition stabilizes and patients usually survive into adulthood. As RTT occurs almost exclusively in females, it has been proposed that RTT is caused by an X-linked dominant mutation with lethality in hemizygous males(3-8). Previous exclusion mapping studies using RTT families mapped the locus to Xq28 (refs 6,7,9-11). Using a systematic gene screening approach, we have identified mutations in the gene (MECP2) encoding X-linked methyl-CpG-binding protein 2 (MeCP2) as the cause of some Eases of RTT. MeCP2 selectively binds CpG dinucleotides in the mammalian genome and mediates transcriptional repression through interaction with histone deacetylase and the corepressor SIN3A (refs 12,13). In 5 of 21 sporadic patients, we found 3 de novo missense mutations in the region encoding the highly conserved methyl-binding domain (MBD) as well as a de novo frameshift and a de novo nonsense mutation, both of which disrupt the transcription repression domain (TRD). In two affected half-sisters of a RTT family, we found segregation of an additional missense mutation not detected in their obligate carrier mother. This suggests that the mother is a germline mosaic for this mutation. Our study reports the first disease-causing mutations in RTT and points to abnormal epigenetic regulation as the mechanism underlying the pathogenesis of RTT.", 
"The discovery of numerous hypermethylated promoters of tumour-suppressor genes, along with a better understanding of gene-silencing mechanisms, has moved DNA methylation from obscurity to recognition as an alternative mechanism of tumour-suppressor inactivation in cancer. Epigenetic events can also facilitate genetic damage, as illustrated by the increased mutagenicity of 5-methylcytosine and the silencing of the MLH1 mismatch repair gene by DNA methylation in colorectal tumours. We review here current mechanistic understanding of the role of DNA methylation in malignant transformation, and suggest Knudson's two-hit hypothesis should now be expanded to include epigenetic mechanisms of gene inactivation.", 
"Densely methylated DNA associates with transcriptionally repressive chromatin characterized by the presence of underacetylated histones(1,2). Recently, these two epigenetic processes have been dynamically linked. The methyl-CpG-binding protein MeCP2 appears to reside in a complex with histone deacetylase activity(3,4). MeCP2 can mediate formation of transcriptionally repressive chromatin on methylated promoter templates in vitro, and this process can be reversed by trichostatin A (TSA), a specific inhibitor of histone deacetylase(3-5). Little is known, however, about the relative roles of methylation and histone deacetylase activity in the stable inhibition of transcription on densely methylated endogenous promoters, such as those for silenced alleles of imprinted genes(6), genes on the female inactive X chromosome(7) and tumour-suppressor genes inactivated in cancer cells(8,9). We show here that the hypermethylated genes MLH1, TIMP3 (TIMP3), CDKN2B (INK4B, p15) and CDKN2A (INK4, p16) cannot be transcriptionally reactivated with TSA alone in tumour cells in which we have shown that TSA alone can upregulate the expression of non-methylated genes. Following minimal demethylation and slight gene reactivation in the presence of low dose 5-aza-2'deoxycytidine (5Aza-dC), however, TSA treatment results in robust re-expression of each gene. TSA does not contribute to demethylation of the genes, and none of the treatments alter the chromatin structure associated with the hypermethylated promoters. Thus, although DNA methylation and histone deacetylation appear to act as synergistic layers for the silencing of genes in cancer, dense CpG island methylation is dominant for the stable maintenance of a silent state at these loci.", 
" ", 
"'Viable yellow' (A(vy)/alpha) mice are larger, obese, hyperinsulinemic, more susceptible to cancer, and, on average, shorter lived than their non-yellow siblings. They are epigenetic mosaics ranging from a yellow phenotype with maximum ectopic agouti overexpression, through a continuum of mottled agouti/yellow phenotypes with partial agouti overexpression, to a pseudoagouti phenotype with minimal ectopic expression. Pseudoagouti A(vy)/a mice are lean, healthy, and longer lived than their yellow siblings. Here we report that feeding pregnant black a/a dams methyl-supplemented diets alters epigenetic regulation of agouti expression in their offspring, as indicated by increased agouti/black mottling in the direction of the pseudoagouti phenotype, We also present confirmatory evidence that epigenetic phenotypes are maternally heritable. Thus A(vy) expression, already known to be modulated by imprinting, strain-specific modification, and maternal epigenetic inheritance, is also modulated by maternal diet. These observations suggest, at least in this special case, that maternal dietary supplementation may positively affect health and longevity of the offspring, Therefore, this experimental system should be useful for identifying maternal factors that modulate epigenetic mechanisms, especially DNA methylation, in developing embryos.", 
"The yeast Sir2 protein regulates epigenetic gene silencing and as a possible antiaging effect it suppresses recombination of rDNA. Studies involving cobB, a bacterial SIR2-like gene, have suggested it could encode a pyridine nucleotide transferase. Here five human sirtuin cDNAs are characterized. The SIRT1 sequence has the closest homology to the S. cerevisiae Sir2p. The SIRT4 and SIRT5 sirtuins more closely resemble prokaryotic sirtuin sequences. The five human sirtuins are widely expressed in fetal and adult tissues. Recombinant E. coli cobT and cobB proteins each showed a weak NAD-dependent mono-ADP-ribosyltransferase activity using 5,6-dimethylbenzimidazole as a substrate. Recombinant E. coli cobB and human SIRT2 sirtuin proteins were able to cause radioactivity to be transfered from [P-32]NAD to bovine serum albumin (BSA). When a conserved histidine within the human SIRT2 sirtuin was converted to a tyrosine, the mutant recombinant protein was unable to transfer radioactivity from [P-32]NAD to BSA. These results suggest that the sirtuins may function via mono-ADP-ribosylation Of proteins. (C) 1999 Academic Press.", 
"Gene activation in eukaryotes requires chromatin remodeling complexes like Swi/Snf and histone acetylases like SAGA. How these factors are recruited to promoters is not yet understood. Using CHIP, we measured recruitment of Swi/Snf, SAGA, the repressor Ash1p, and transcription factors Swi5p and SBF to the HO endonuclease promoter as cells progress through the yeast cell cycle. Swi5p's entry into nuclei at the end of anaphase recruits Swi/Snf, which then recruits SAGA. These two factors then facilitate SBF's binding. Ash1p, which only accumulates in daughter cell nuclei, binds to HO soon after Swi5p and aborts recruitment of Swi/Snf, SAGA, and SBF. Swi5p remains at HO for only 5 min. Swi/Snf's and SAGA's subsequent persistence at HO is self sustaining and constitutes an epigenetic memory of HO's transient interaction with Swi5p.", 
"Altering cytosine methylation by genetic means leads to a variety of developmental defects in mice(1), plants(2-5) and fungi(6,7) Deregulation of cytosine methylation also has a role in human carcinogenesis(8). In some cases, these defects have been tied to the inheritance of epigenetic alterations (such as chromatin imprints and DNA methylation patterns) that do not involve changes in DNA sequence(3,8-10). Using a forward genetic screen, we identified a gene (DDM1, decrease in DNA methylation) from the flowering plant Arabidopsis thaliana required to maintain normal cytosine methylation patterns(11). Additional ddm1 alleles (som4, 5, 6, 7, 8) were isolated in a selection for mutations that relieved transgene silencing(12) (E.J.R., unpublished data). Loss of DDM1 function causes a 70% reduction of genomic cytosine methylation, with most of the immediate hypomethylation occurring in repeated sequences(11). In contrast, many low-copy sequences initially retain their methylation in ddm1 homozygotes, but lose methylation over time as the mutants are propagated through multiple generations by self-pollination(3,13). The progressive effect of ddm1 mutations on low-copy sequence methylation suggests that ddm1 mutations compromise the efficiency of methylation of newly incorporated cytosines after DNA replication. In parallel with the slow decay of methylation during inbreeding, ddm1 mutants accumulate heritable alterations (mutations or stable epialleles) at dispersed sites in the genome that lead to morphological abnormalities(3,5,14). Here we report that DDM1 encodes a SWI2/SNF2-like protein, implicating chromatin remodelling as an important process for maintenance of DNA methylation and genome integrity.", 
"Chromatin assembly factor 1 (CAF-1) is required for inheritance of epigenetically determined chromosomal states in vivo and promotes assembly of chromatin during DNA replication in vitro. Herein, we demonstrate that after DNA replication, replicated, but not unreplicated, DNA is also competent for CAF-1-dependent chromatin assembly. The proliferating cell nuclear antigen (PCNA), a DNA polymerase clamp, is a component of the replication-dependent marking of DNA for chromatin assembly. The clamp loader, replication factor C (RFC), can reverse this mark by unloading PCNA from the replicated DNA. PCNA binds directly to p150, the largest subunit of CAF-1, and the two proteins colocalize at sites of DNA replication in cells. We suggest that PCNA and CAF-1 connect DNA replication to chromatin assembly and the inheritance of epigenetic chromosome states.", 
"A handful of autosomal genes in the mammalian genome are inherited in a silent state from one of the two parents, and in a fully active form from the other, thereby rendering the organism functionally hemizygous for imprinted genes. To date 19 imprinted genes have been identified; 5 are expressed from the maternal chromosome while the rest are expressed from the paternal chromosome. Allele-specific methylation of CpG residues, established in one of the germlines and maintained throughout embryogenesis, has been clearly implicated in the maintenance of imprinting in somatic cells. Although the function of imprinting remains a subject of some debate, the process is thought to have an important role in regulating the rate of fetal growth.", 
"Members of the Plasmodium falciparum var gene family encode clonally variant adhesins, which play an important role in the pathogenicity of tropical malaria. Here we employ a selective panning protocol to generate isogenic P falciparum populations with defined adhesive phenotypes for CD36, ICAM-1 and CSA, expressing single and distinct var gene variants. This technique has established the framework for examining var gene expression, its regulation and switching. It was found that var gene switching occurs irt situ. Ubiquitous transcription of all var gene variants appears to occur in early ring stages. However, var gene expression is tightly regulated in trophozoites and is exerted through a silencing mechanism. Transcriptional control is mutually exclusive in parasites that express defined adhesive phenotypes. lit situ var gene switching is apparently mediated at the level of transcriptional initiation, as demonstrated by nuclear run-on analyses. Our results suggest that an epigenetic mechanism(s) is involved in var gene regulation.", 
"Nuclear receptors (NRs) are ligand-inducible transcription factors that mediate complex effects on development, differentiation and homeostasis. They regulate the transcription of their target genes through binding to cognate DNA sequences as homodimers or heterodimers, The molecular mechanisms underlying transcriptional activation by NRs are still poorly understood, although intermediary factors (mediators) appear to be involved in mediating the transactivation functions of NRs, TIF1 has been identified previously as a protein that interacts specifically with the ligand binding domain of several nuclear receptors, both in yeast and in vitro. The characteristics of these interactions have led us to suggest that TIF1 might be a mediator of the NR ligand-inducible activation function AF-2, Using a two-hybrid screening in yeast, we have now identified two TLFP-binding proteins, mHP1 alpha and mMOD1, that are mouse homologues of the Drosophila heterochromatinic protein 1. Using mHP1 alpha as a bait in a second two-hybrid screening, we have isolated cDNAs encoding proteins that are also very likely to be involved in chromatin structure and function, as well as a protein structurally and functionally related to TIF1 (renamed TLF1 alpha), which was named TIF1 beta. Here we discuss how the function of members of the TIF1 family in the control of transcription could be exerted at the level of the structure of the chromatin template.", 
"The past few years have seen a wider acceptance of a role for DNA methylation in cancer. This can be attributed to three developments. First, the documentation of the over-representation of mutations at CpG dinucleotides has convincingly implicated DNA methylation in the generation of oncogenic point mutations. The second important advance has been the demonstration of epigenetic silencing of tumor suppressor genes by DNA methylation. The third development has been the utilization of experimental methods to manipulate DNA methylation levels. These studies demonstrate that DNA methylation changes in cancer cells are not mere by-products of malignant transformation, but can play an instrumental role in the cancer process. It seems clear that DNA methylation plays a variety of roles in different cancer types and probably at different stages of oncogenesis. DNA methylation is intricately involved in a wide diversity of cellular processes. Likewise, it appears to exert its influence on the cancer process through a diverse array of mechanisms. It is our task not only to identify these mechanisms, but to determine their relative importance for each stage and type of cancer. Our hope then will be to translate that knowledge into clinical applications.", 
"The inactive X chromosome differs from the active X in a number of ways; some of these, such as allocyclic replication and altered histone acetylation, are associated with all types of epigenetic silencing, whereas others, such as DNA methylation, are of more restricted use. These features are acquired progressively by the inactive X after onset of initiation. Initiation of X-inactivation is controlled by the X-inactivation center (Xic) and influenced by the X chromosome controlling element (Xce), which causes primary nonrandom X-inactivation. Other examples of nonrandom X-inactivation are also presented in this review. The definition of a major role for Xist, a noncoding RNA, in X-inactivation has enabled investigation of the mechanism leading to establishment of the heterochromatinized X-chromosome and also of the interactions between X-inactivation and imprinting as well as between X-inactivation and developmental processes in the early embryo.", 
"The centromere is required to ensure the equal distribution of replicated chromosomes to daughter nuclei. Centromeres are frequently associated with heterochromatin, an enigmatic nuclear component that causes the epigenetic transcriptional repression of nearby marker genes (position-effect variegation of silencing). The process of chromosome segregation by movement along microtubules to spindle poles is highly conserved, yet the putative cis-acting centromeric DNA sequences bear little or no similarity across species. Recently, studies in several systems have revealed that the centromere itself might be epigenetically regulated and that the higher-order structure of the underlying heterochromatin contributes to centromere function and kinetochore assembly.", 
"The chrome and SET domains are conserved sequence moths present in chromosomal proteins that function in epigenetic control of gene expression, presumably by modulating higher order chromatin, Based on sequence information from the SET domain, we have isolated human (SUV39H1) and mouse (Suv39h1) homologues of the dominant Drosophila modifier of position-effect-variegation (PEV) Su(var)3-9. Mammalian homologues contain, in addition to the SET domain, the characteristic chrome domain, a combination that is also preserved in the Schizosaccharyomyces pombe silencing factor clr4. Chromatin-dependent gene regulation is demonstrated by the potential of human SUV39H1 to increase repression of the pericentromeric white marker gene in transgenic flies. Immunodetection of endogenous Suv39h1/SUV39H1 proteins in a variety of mammalian cell lines reveals enriched distribution at heterochromatic foci during interphase and centromere-specific localization during metaphase, In addition, Suv39h1/SUV39H1 proteins associate with M31, currently the only other characterized mammalian SU(VAR) homologue, These data indicate the existence of a mammalian SU(VAR) complex and define Suv39h1/SUV39H1 as novel components of mammalian higher order chromatin.", 
"post-transcriptional gene silencing (PTGS) is a homology-dependent process that reduces cytoplasmic RNA levels. In several experimental systems, there is also an association of PTGS with methylation of DNA. To investigate this association, we used plants carrying a transgene encoding the green fluorescent protein (GFP), Gene silencing was induced using potato virus X RNA vectors carrying parts of the coding sequence or the promoter of the GFP transgene. In each instance, homology-based, RNA-directed methylation was associated with silencing. When the GFP-transcribed region was targeted, PTGS affected both transgene and viral RNA revels. When methylation was targeted to a promoter region, transgene RNA levels were reduced; however, viral RNA revels were unaffected. For comparison, we induced PTGS of the gene encoding the endogenous ribulose-1,5-bisphosphate carboxylase oxygenase (Rubisco) small subunit (rbcS) by inoculation with potato virus X-rbcS, In this example, no methylation of the rbcS DNA was associated with the reduction in rbcS transcript levels, and viral RNA levels were unaffected. Finally, we investigated DNA methylation by using GFP-transformed plants in which PTGS was induced by localized introduction of a T-DNA carrying GFP sequences. In these plants, there was methylation of a GFP transgene associated with systemic spread of a gene-silencing signal from the infiltrated part of the plant. This transgene methylation was not affected when systemic PTGS was blocked by suppressors of silencing encoded by potato virus Y and cucumber mosaic virus. Combined, these data support an epigenetic model of PTGS in which transgene methylation is associated with an RNA-DNA interaction that ensures that PTGS is maintained.", 
"Although the link between the BRCA1 tumour-suppressor gene and hereditary breast and ovarian cancer is established(1-5), the role, if any, of BRCA1 in non-familial cancers is unclear. BRCA1 mutations are rare in sporadic cancers(6-8), but loss of BRCA1 resulting from reduced expression or incorrect subcellular localization(9,10) is postulated to be important in non-familial breast and ovarian cancers. Epigenetic loss, however, has not received general acceptance due to controversy regarding the subcellular localization of BRCA1 proteins, reports of which have ranged from exclusively nuclear(11-15), to conditionally nuclear(10), to the ER/golgi(16), to cytoplasmic invaginations into the nucleus(17). In an attempt to resolve this issue, we have comprehensively characterized 19 anti-BRCA1. antibodies. These reagents detect a 220-kD protein localized in discrete nuclear foci in all epithelial cell lines, including those derived from breast malignancies. Immunohistochemical staining of human breast specimens also revealed BRCA1 nuclear foci in benign breast, invasive lobular cancers and low-grade ductal carcinomas. Conversely, BRCA1 expression was reduced or undetectable in the majority of high-grade, ductal carcinomas, suggesting that absence of BRCA1 may contribute to the pathogenesis of a significant percentage of sporadic breast cancers.", 
"CpG island hypermethylation is known to be associated with gene silencing in cancer. This epigenetic event is generally accepted as a stochastic process in tumor cells resulting from aberrant DNA methyltransferase (DNA-MTase) activities. Specific patterns of CPG island methylation could result from clonal selection of cells having growth advantages due to silencing of associated tumor suppressor genes. Alternatively, methylation patterns may be determined by other, as yet unidentified factors, To explore further the underlying mechanisms, we developed a novel array-based method, called differential methylation hybridization (DMH), which allows a genome-wide screening of hypermethylated CpG islands in tumor cells. DMH was used to determine the methylation status of >276 CpG island loci in a group of breast cancer cell lines. Between 5 and 14% of these loci were hypermethylated extensively in these cells relative to a normal control. Pattern analysis of 30 positive loci by Southern hybridization indicated that CpG islands might differ in their susceptibility to hypermethylation, Loci exhibiting preexisting methylation in normal controls were more susceptible to de novo methylation in these cancer cells than loci without this condition, In addition, these cell lines exhibited different intrinsic abilities to methylate CpG islands not directly associated with methyltransferase activities. Our study provides evidence that, aside from random DNA-MTase action, additional cellular factors exist that govern aberrant methylation in breast cancer cells.", 
"Genomic reprogramming of primordial germ cells (PGCs), which includes genome-wide demethylation, prevents aberrant epigenetic modifications from being transmitted to subsequent generations, This process also ensures that homologous chromosomes first acquire an identical epigenetic status before an appropriate switch in the imprintable loci in the female and male germ lines. Embryonic germ (EG) cells have a similar epigenotype to PGCs from which they are derived, We used EG cells to investigate the mechanism of epigenetic modifications in the germ line by analysing the effects on a somatic nucleus in the EG-thymic lymphocyte hybrid cells. There were striking changes in methylation of the somatic nucleus, resulting in demethylation of several imprinted and non-imprinted genes, These epigenetic modifications were heritable and affected gene expression as judged by re-activation of the silent maternal allele of Peg1/Mest imprinted gene in the somatic nucleus. This remarkable change in the epigenotype of the somatic nucleus is consistent with the observed pluripotency of the EG-somatic hybrid cells as they differentiated into a variety of tissues in chimeric embryos. The epigenetic modifications observed in EG-somatic cell hybrids in vitro are comparable to the reprogramming events that occur during germ cell development.", 
"To determine which CD3 components are required for early T cell development, we generated mice with a targeted mutation of the CD3-epsilon gene and characterized their T cell populations relative to those found in CD3-zeta/eta- and recombinase activating gene (RAG)-deficient mice, In the absence of intact CD3-epsilon subunit, thymocytes do not progress beyond the CD44(-/low)CD25(+) triple-negative stage and appear to be arrested at the very same developmental control point as RAG-deficient thymocytes, In contrast, the disruption of the CD3-zeta/eta gene does not totally abrogate the progression through this control point, CD3-epsilon-deficient thymocytes do rearrange their T cell receptor (TCR) beta gene segments and produce low levels of full-length TCR beta transcripts. Taken together, these results establish an essential role for the CD3-epsilon gene products during T cell development and further suggest that the CD3-epsilon polypeptides start to exert their function as part of a pre-TCR through which CD44(-/low)CD25(+) triple-negative cells monitor the occurrence of productive TCR beta gene rearrangements. Finally, the absence of intact CD3-epsilon polypeptides had no discernible effect on the completion of TCR gamma and TCR delta gene rearrangements, emphasizing that they are probably not subjected to the same epigenetic controls as those operating on the expression of TCR alpha and beta genes.", 
"The constitutive DNase I hypersensitive site at the 5' end of the chicken beta-globin locus marks the boundary of the active chromatin domain in erythroid cells. The DNA sequence containing this site has the properties of an insulator, as shown by its ability in stable transformation experiments to block enhancer-promoter interaction when it lies between the two, but not when it lies outside, and to protect against position effects in Drosophila. We now show that the chicken insulator can protect a stably integrated gene, which is otherwise subject to great variability of expression, from chromatin-mediated repression in cell culture. When the integrated reporter gene is surrounded by insulator elements, stably transformed cell lines display consistent enhancer-dependent expression levels, in accord with the strength of the enhancer. In the absence of insulators, long-term nonselective propagation of cells carrying the integrated reporter gene results in gradual extinction of the reporter's expression, with expression patterns from tandemly repeated inserted genes suggesting that the extinction of adjacent genes is coupled. We show that the uninsulated reporter genes, in addition to becoming transcriptionally inactive, lose several epigenetic hallmarks of active chromatin, including nuclease accessibility, DNA hypomethylation, and histone hyperacetylation during time in culture. Treatment with inhibitors of histone deacetylase or DNA methylation reverses the extinction of the uninsulated genes. Extinction is completely prevented by flanking the reporter construct with insulators. Furthermore, in contrast to the uninsulated reporter genes, chromatin over the insulated genes retains nuclease accessibility and histone hyperacetylation. However, there is no clear correlation between the presence of the insulators and the level of DNA methylation. This leads us to propose a model for the insulator's ability to protect against extinction in the transformed cell lines and to function as a chromatin boundary for the chicken beta-globin locus in normal erythroid cells.", 
"Kruppel-associated box (KRAB) domains are present in approximately one-third of all human zinc finger proteins (ZFPs) and are potent transcriptional repression modules. We have previously cloned a corepressor for the KRAB domain, KAP-1, which is required for KRAB-mediated repression in vivo. To characterize the repression mechanism utilized by KAP-1, we have analyzed the ability of KAP-1 to interact with murine (M31 and M32) and human (HP1 alpha and HP1 gamma) homologues of the HPI protein family, a class of nonhistone heterochromatin-associated proteins with a well-established epigenetic gene silencing function in Drosophila, In vitro studies confirmed that KAP-1 is capable of directly interacting with M31 and hHP1 alpha, which are normally found in centromeric heterochromatin, as well as M32 and hHP1 gamma, both of which are found in euchromatin, Mapping of the region in KAP-1 required for HPI interaction showed that amino acid substitutions which abolish HP1 binding in vitro reduce KAP-1 mediated repression in vivo. We observed colocalization of KAP-1 with M31 and M32 in interphase nuclei, lending support to the biochemical evidence that M31 and M32 directly interact with KAP-1, The colocalization of KAP-1 with M31 is sometimes found in subnuclear territories of potential pericentromeric heterochromatin, whereas colocalization of KAP-1 and M32 occurs in punctate euchromatic domains throughout the nucleus. This work suggests a mechanism for the recruitment of HP1-like gene products by the KRAB-ZFP-KAP-1 complex to specific loci within the genome through formation of heterochromatin-like complexes that silence gene activity. We speculate that gene-specific repression may be a consequence of the formation of such complexes, ultimately leading to silenced genes in newly formed heterochromatic chromosomal environments.", 
"Flower pigmentation patterns were scored in 185 sense Chalcone synthase (Chs) transgenotes and 85 antisense Chs transgenotes; upon first flowering, 139 (75%) of sense transgenotes were found to be phenotypically altered, as were 70 (82%) of the antisense transgenotes. The observed patterns document the range of phenotypic variations that occur, as well as confirm and extend the finding that sense Chs constructs produce several types of morphology-based flower pigmentation patterns that antisense Chs constructs do not. Long-term monitoring for epigenetic variations in one population of 44 sense Chs transgenotes showed that 43 (98%) were capable of producing a cosuppression phenotype. The primary determinant of sense-specific patterns of cosuppression of Chs was found to be the repetitiveness and organization pattern of the transgene, not 'position effects' by, or 'readthrough' from, flanking plant DNA sequences. The degree of cosuppression observed in progeny of transgenotes carrying multiple, dispersed copies as compared to that observed with a single copy of the transgene suggests that sense cosuppression of Chs is subject to a transgene dosage effect.", 
"A transgenic gpt(+) Chinese hamster cell line (G12) was found to be susceptible to carcinogenic nickel-induced inactivation of gpt expression without mutagenesis or deletion of the transgene. Many nickel-induced 6-thioguanine-resistant variants spontaneously reverted to actively express gpt, as indicated by both reversion assays and direct enzyme measurements. Since reversion was enhanced in many of the nickel-induced variant cell lines following 24-h treatment with the demethylating agent 5-azacytidine, the involvement of DNA methylation in silencing gpt expression was suspected. This was confirmed by demonstrations of increased DNA methylation, as well as by evidence indicating condensed chromatin and heterochromatinization of the gpt integration site in 6 thioguanine-resistant cells. Upon reversion to active gpt expression, DNA methylation and condensation are lost. We propose that DNA condensation and methylation result in heterochromatinization of the gpt sequence with subsequent inheritance of the now silenced gene. This mechanism is supported by direct evidence showing that acute nickel treatment of cultured cells, and of isolated nuclei in vitro, can indeed facilitate gpt sequence-specific chromatin condensation. Epigenetic mechanisms have been implicated in the actions of some nonmutagenic carcinogens, and DNA methylation changes are now known to be important in carcinogenesis. This paper further supports the emerging theory that nickel is a human carcinogen that can alter gene expression by enhanced DNA methylation and compaction, rather than by mutagenic mechanisms.", 
"In vitro manipulation of preimplantation mammalian embryos can influence differentiation and growth at later stages of development, In the mouse, culture of embryonic stem (ES) cells affects their totipotency and may give rise to fetal abnormalities, To investigate whether this is associated with epigenetic alterations in imprinted genes, we analysed two maternally expressed genes (Igf2r, H19) and two paternally expressed genes (Igf2, U2af1-rs1) in ES cells and in completely ES cell-derived fetuses, Altered allelic methylation patterns were detected in all four genes, and these were consistently associated with allelic changes in gene expression, All the methylation changes that had arisen in the ES cells persisted on in vivo differentiation to fetal stages, Alterations included loss of methylation with biallelic expression of U2af1-rs1, maternal methylation and predominantly maternal expression of Igf2, and biallelic methylation and expression of Igf2r In many of the ES fetuses, the levels of H19 expression were strongly reduced, and this biallelic repression was associated with biallellic methylation of the H19 upstream region, Surprisingly, biallelic H19 repression was not associated with equal levels of Igf2 expression from both parental chromosomes, but rather with a strong activation of the maternal Igf2 allele, ES fetuses derived from two of the four ES lines appeared developmentally compromised, with polyhydramnios, poor mandible development and interstitial bleeding and, in chimeric fetuses, the degree of chimerism correlated with increased fetal mass, Our study establishes a model for how early embryonic epigenetic alterations in imprinted genes persist to later developmental stages, and are associated with aberrant phenotypes.", 
"Polycomb group (PcG) and trithorax group (trxG) gene products are responsible for the maintenance of repressed and active expression patterns of many developmentally important regulatory genes including the homeotic genes. In Drosophila embryos, Polycomb protein and the trxG protein GAGA factor colocalize at the Fab-7 DNA element of the bithorax complex. In transgenic lines, the Fab-7 element induces extensive silencing on a flanking GAL4-driven lacZ reporter and mini-white genes. However, a short single pulse of GAL4 during embryogenesis is sufficient to release PcG-dependent silencing from the transgene. Such an activated state of Fab-7 is mitotically inheritable through development and can be transmitted in a GAL4-independent manner to the subsequent generations through female meiosis. Thus, Fab-7 is a switchable chromosomal element, which can convey memory of epigenetically determined active and repressed chromatin states.", 
"Methylation of cytosine residues in DNA provides a mechanism of gene control. There are two classes of methyltransferase in Arabidopsis; one has a carboxy-terminal methyltransferase domain fused to an amino-terminal regulatory domain and is similar to mammalian methyltransferases. The Second class apparently lacks an amino-terminal domain and is less well conserved. Methylcytosine can occur at any cytosine residue, but it is likely that clonal transmission of methylation patterns only occurs for cytosines in strand-symmetrical sequences CpG and CpNpG. In plants, as in mammals, DNA methylation has dual roles in defense against invading DNA and transposable elements and in gene regulation. Although originally reported as having no phenotypic consequence, reduced DNA methylation disrupts normal plant development.", 
"The trilaminar kinetochore directs the segregation of chromosomes in mitosis and meiosis. Despite its importance, the molecular architecture of this structure remains poorly understood [1]. The best known component of the kinetochore plates is CENP-C, a protein that is required for kinetochore assembly [2], but whose molecular role in kinetochore structure and function is unknown. Here we have raised for the first time monospecific antisera to CENP-A [3], a 17 kD centromere-specific histone variant that is 62% identical to the carboxy-terminal domain of histone H3 [4,5] and that resembles the yeast centromeric component CSE4 [6]. We have found by simultaneous immunofluorescence with centromere antigens of known ultrastructural location that CENP-A is concentrated in the region of the inner kinetochore plate at active centromeres. Because CENP A was previously shown to co-purify with nucleosomes [7], our data suggest a specific nucleosomal substructure for the kinetochore. In human cells, these kinetochore-specific nucleosomes are enriched in alpha-satellite DNA [8]. However, the association of CENP-A with neocentromeres lacking detectable alpha-satellite DNA, and the lack of CENP-A association with alpha-satellite-rich inactive centromeres of dicentric chromosomes together suggest that CENP-A association with kinetochores is unlikely to be determined solely by DNA sequence recognition. We speculate that CENP-A binding could be a consequence of epigenetic tagging of mammalian centromeres.", 
"Nucleolar dominance is an epigenetic phenomenon that describes nucleolus formation around rRNA genes inherited from only one progenitor of an interspecific hy;brid or allopolyploid. The phenomenon is widespread, occurring in plants, insects, amphibians, and mammals, yet its molecular basis remains unclear. We have demonstrated nucleolar dominance in three allotetraploids of the plant genus Brassica. In Brassica napus, accurately initiated pre-rRNA transcripts from one progenitor, Brassica rapa are detected readily, whereas transcripts from the similar to 3000 rRNA genes inherited from the other progenitor, Brassica oleracea, are undetectable. Nuclear run-on confirmed that dominance is controlled at the level of transcription. Growth of B. napus seedlings on 5-aza-2'-deoxycytidine to inhibit cytosine methylation caused the normally silent, under-dominant B. oleracea rRNA genes to become expressed to high levels. The histone deacetylase inhibitors sodium butyrate and trichostatin A also de-epressed silent rRNA genes. These results reveal an enforcement mechanism for nucleolar dominance in which DNA methylation and histone modifications combine to regulate rRNA gene loci spanning tens of megabase pairs of DNA.", 
"Genomic imprinting is an epigenetic chromosomal modification in the gamete or zygote causing preferential expression of a specific parental allele in somatic cells of the offspring. We and others have identified three imprinted human genes on 11p15.5, IGF2 (refs 1-4), H19 (refs 1,5), and p57(KIP2) (ref. 6), although the latter gene is separated by 700 kb from the other two, and it is unclear whether there are other imprinted genes within this large interval. We previously mapped an embryonal tumour suppressor gene to this region(7), as well as five balanced germline chromosomal rearrangement breakpoints from patients with Beckwith-Wiedemann syndrome (BWS)(8), a condition characterized by prenatal overgrowth and cancer. We isolated the upstream exons of the previously identified gene KVLQT1, which causes the familial cardiac defect long-QT (LQT) syndrome. We found that KVLQT1 spans much of the interval between p57(KIP2) and IGF2, and that it is also imprinted. We demonstrated that the gene is disrupted by chromosomal chromosomal translocation in an embryonal rhabdoid tumour. Furthermore, the lack of parent-of-origin effect in LQT syndrome appears to be due to relative lack of imprinting in the affected tissue, cardiac muscle, representing a novel mechanism for variable penetrance of a human disease gene.", 
"A multisubunit cohesin complex holds sister chromatids together after DNA replication. Using chromatin immunoprecipitation, we detected cohesin association with centromeres and with discrete sites along chromosome arms from S phase until metaphase in S. cerevisiae, Short DNA sequences (130-280 bp) are sufficient to confer cohesin association. Cohesin association with a centromere depends on Mif2p, the centromere binding factor CBF3, and a centromere-specific histone variant, Cse4p. Because only active centromeres confer cohesin association with centromeric DNA, we suggest that cohesin is recruited by the same chromatin structure that confers the attachment of microtubules. Propagation of this structure might be partly epigenetic. Finally, cohesion associated with minimal centromeres is insufficient to resist the splitting force exerted by microtubules and appears to be reinforced by cohesion provided by their flanking DNA sequences.", 
"Loss of imprinting (LOI) is an epigenetic alteration of some cancers involving loss of parental origin-specific expression of imprinted genes. We observed LOI of the insulin-like growth factor-ii gene in twelve of twenty-seven informative colorectal cancer patients (44%), as well as in the matched normal colonic mucosa of the patients with LOI in their cancers, and in peripheral blood samples of four patients. Ten of eleven cancers (91%) with microsatellite instability showed LOI, compared with only two of sixteen tumors (12%) without microsatellite instability (P< 0.001). Control patients without cancer showed LOI in colonic mucosa of only two of sixteen cases (12%, P < 0.001) and two of fifteen blood samples (13%, P < 0.001). These data suggest that LOI in tumor and normal tissue identifies most colorectal cancer patients with microsatellite instability in their tumors, and that LOI may identify an important subset of the population with cancer or at risk of developing cancer.", 
"Silencing is an epigenetic form of transcriptional regulation whereby genes are heritably, but not necessarily permanently, inactivated. We have identified the Saccharomyces cerevisiae genes SAS2 and SAS3 through a screen for enhancers of sir1 epigenetic silencing defects. SAS2, SAS3 and a Schizosaccharomyces pombe homologue are closely related to several human genes, including one associated with acute myeloid leukaemia arising from the recurrent translocation t(8;16)(p11;p13) and one implicated in HIV-1 Tat interactions. All of these genes encode proteins with an atypical zinc finger and well-conserved similarities to acetyltransferases. Sequence similarities and yeast mutant phenotypes suggest that SAS-like genes function in transcriptional regulation and cell-cycle exit and reveal novel connections between transcriptional silencing and human disease.", 
"The multisubunit MSL dosage compensation complex binds to hundreds of sites along the Drosophila single male X chromosome, mediating its hypertranscription, The male X chromosome is also coated with noncoding roX RNAs. When either msl3, mle, or mof is mutant, a partial MSL complex is bound at only similar to 35 unusual sites distributed along the X, We show that two of these sites are the roX1 and roX2 genes and postulate that one of their functions is to provide entry sites for the MSL complex to recognize the X chromosome. The roX1 gene provides a nucleation site for extensive spreading of the MSL complex into flanking chromatin even when moved to an autosome. The spreading can occur in cis or in trans between paired homologs. We present a model for how the dosage compensation complex recognizes X chromatin.", 
"Defective DNA mismatch repair in human turners leads to genome-wide instability of microsatellite repeats and a molecular phenotype referred to as microsatellite instability (MSI), MSI has been reported in a variety of cancers and is a consistent feature of tumors from patients with hereditary non-polyposis colorectal cancer. Approximately 20% of cancers of the uterine endometrium, the fifth most common cancer of women world-wide, exhibit MSI. Although the frequency of MSI is higher in endometrial cancers than in any other common malignancy, the genetic basis of MSI in these tumors has remained elusive, We investigated the role that methylation of the MLH1 DNA mismatch repair gene plays in the genesis of MSI in a large series of sporadic endometrial cancers. The MLH1 promoter was methylated in 41 of 53 (77%) MSI-positive cancers investigated. In MSI-negative tumors on the other hand, there was evidence for limited methylation in only one of 11 tumors studied. Immunohistochemical investigation of a subset of the tumors revealed that methylation of the MLH1 promoter in MSI-positive tumors was associated with loss of MLH1 expression. Immunohistochemistry proved that two MSI-positive tumors lacking MLH1 methylation failed to express the MSH2 mismatch repair gene. Both of these cancers came from women who had family and medical histories suggestive of inherited cancer susceptibility. These observations suggest that epigenetic changes in the MLH1 locus account for MSI in most cases of sporadic endometrial cancers and provide additional evidence that the MSH2 gene may contribute substantially to inherited forms of endometrial cancer.", 
"Several lines of evidence strongly suggest that DNA methylation is involved in embryo development, Perhaps the most direct evidence comes from experiments with methyltransferase deficient mice. Embryos that express low levels of the maintenance methyltransferase do not develop to term and die at the 5 to 20 somite stage corresponding to the level of the enzyme. In the mouse, dramatic methylation changes have been observed during the early steps of embryo development. Most genes are subject to a process of active demethylation starting promptly after fertilization. Except for a small number of methylated CpG sites in imprinted genes the vast majority of the sites are unmethylated by the stage of cavitation (16 cell). Such genome-wide demethylation may signify an erasure of epigenetic information originating in the highly differentiated gametes. This erasure may be essential for the establishment of a pluripotent state, before specific cell lineages can be determined. The process of laying down a new developmental program involves, initially, global de novo methylation at the stage of pregastrulation followed by gene specific demethylations associated with the onset of activity of these genes. CpG islands characteristic of housekeeping genes, appear to be protected from the global de novo methylation. An exception to this rule is the hypermethylation of CpG islands in X-linked housekeeping genes on the inactive X chromosome and of specific differentially methylated CpG sites in imprinted genes. Primordial germ cells escape the global de novo methylation which takes place at the pregastrula stage and undergo a very similar de novo methylation process in the differentiated gonads (15.5-18.5 days post coitum), forming the methylation patterns which are specific to the gametes. Specific demethylations then form a terminal methylation pattern which is then clonaly inherited in the soma and erased after fertilization.", 
"During the development of a multicellular organism from a zygote, a large number of epigenetic interactions take place on every level of suborganismal organization. This raises the possibility that the system of epigenetic interactions may compensate or ''buffer'' some of the changes that occur as mutations on its lowest levels, and thus stabilize the phenotype with respect to mutations. This hypothetical phenomenon will be called ''epigenetic stability.'' Its potential importance stems from the fact that phenotypic variation with a genetic basis is an essential prerequisite for evolution. Thus, variation in epigenetic stability might profoundly affect attainable rates of evolution. While representing a systemic property of a developmental system, epigenetic stability might itself be genetically determined and thus be subject to evolutionary change, Whether or not this is the case should ideally be answered directly, that is, by experimentation. The time seals involved and our insufficient quantitative understanding of developmental pathways will probably preclude such an approach in the foreseeable future. Preliminary answers are sought here by using a biochemically motivated model of a small bur central part of a developmental pathway. Modeled are sets of transcriptional regulators that mutually regulate each other's expression and thereby form stable gene expression patterns. Such gene-expression patterns, crucially involved in determining developmental pattern formation events, are most likely subject to strong stabilizing natural selection, After long periods of stabilizing selection. the fraction of mutations causing changes in gene-expression pattern is substantially reduced in the model. Epigenetic stability has increased. This phenomenon is found for widely varying regulatory scenarios among transcription factor genes. Its discussed that only epistatic (nonlinear) gene interactions can cause such change in epigenetic stability. Evidence from paleontology, molecular evolution, development, and genetics, consistent with the existence of variation in epigenetic stability, is discussed, The relation of epigenetic stability to developmental canalization is outlined. Experimental scenarios at suggested thar may provide further evidence.", 
"X-chromosome inactivation is the process by which a cell recognizes the presence of two copies of an X chromosome early in the development of XX embryos and chooses one to be active and one to be inactive(1) Although it is commonly believed that the initiation of X inactivation is random, with an equal probability (50:50) that either X chromosome will be the inactive X in a given cell, significant variation in the proportion of cells with either X inactive is observed both in mice heterozygous for alleles at the Xce locus(2) and among normal human females in the population(3-5). Families in which multiple females demonstrate extremely skewed inactivation patterns that are otherwise quite rare in the general population are thought to reflect possible genetic influences on the X-inactivation process(5-7). Here we report a rare cytosine to guanine mutation in the XIST minimal promoter that underlies both epigenetic and functional differences between the two X chromosomes in nine females from two unrelated families. All females demonstrate preferential inactivation of the X chromosome carrying the mutation, suggesting that there is an association between alterations in the regulation of XIST expression and X-chromosome inactivation.", 
"Genomic imprinting is an epigenetic process that results in the preferential silencing of one of the two parental copies of a gene. Although the precise mechanisms by which genomic imprinting occurs are unknown, the tendency of imprinted genes to exist in chromosomal clusters suggests long-range regulation through shared regulatory elements. We characterize a 800-kb region on the distal end of mouse chromosome 7 that contains a cluster of four maternally expressed genes, H19, Mash2, Kvlqt1, and p57(Kip2), as well as two paternally expressed genes, Igf2 and Ins2, and assess the expression and imprinting of Mash2, Kvlqt1, and p57(Kip2) during development in embryonic and extraembryonic tissues. Unlike Igf2 and Ins2, which depend on H19 for their imprinting, Mash2, p57(Kip2), and Kvlqt1 are unaffected by a deletion of the H19 gene region, suggesting that these more telomeric genes are not regulated by the mechanism that controls H19, Igf2, and Ins2. Mutations in human p57(Kip2) have been implicated in Beckwith-Wiedemann syndrome, a disease that has also been associated with loss of imprinting of IGF2. We find, however, that a deletion of the gene has no effect on imprinting within the cluster. Surprisingly, the three maternally expressed genes are regulated very differently by DNA methylation; p57(Kip2) activated, Kvlqt1 is silenced, and Mash2 is unaffected in mice lacking DNA methyltransferase. We conclude that H19 is not a global regulator of imprinting on distal chromosome 7 and that the telomeric genes are imprinted by a separate mechanism(s).", 
"Skeletal myoblasts are derived from paraxial mesoderm, but how myoblasts acquire their identity is still a matter of speculation. The characterization of molecular markers and, in some cases, the analysis of mutations in the corresponding genes, has now made it possible to ask specific questions about this process. Specification of somite cell fate depends on epigenetic factors. Adjacent tissues, such as the neural tube, notochord, dorsal ectoderm and lateral mesoderm, act either positively or negatively on the different myogenic precursor populations in the somite. Candidate molecules for this complex signalling activity include sonic hedgehog and the Wnt proteins as positive signals, and BMP4 as a possible inhibitor. Although it is generally assumed that induction is required, some observations suggest that embryonic cells might have a tendency to undergo myogenesis as a 'default' pathway. By analogy with Drosophila, where the neurogenic genes affect myogenesis, the vertebrate homologues of notch and its ligands could be candidate molecules for a repression or derepression mechanism. Similar studies with cultured muscle cells also implicate other HLH factors as potential inhibitors of the MyoD family and, hence, of inappropriate myogenesis.", 
"Overexpression of chimeric transgenes in plants can trigger post-transcriptional gene silencing that is dependent on epigenetic information and physiological conditions. The current view is that unproductive RNA serves as a crucial signal for gene silencing, although direct evidence is lacking for this theory. A signalling cascade then leads to strongly enhanced turnover of all RNAs that share a critical degree of sequence similarity. The molecular details of the mechanism are, however, insufficiently understood to explain the phenomenon completely and to comprehend its biological significance.", 
" ", 
"Photocarcinogenesis represents the sum of a complex of simultaneous and sequential biochemical events that ultimately lead to the occurrence of skin cancer. These events, initiated by UV radiation of appropriate wavelength, include the formation of DNA photoproducts: DNA repair; mutation of proto-oncogenes and tumor suppressor genes; UV-production of radical species with subsequent effects on mutation and extra-nuclear function; and other epigenetic events that influence the course of carcinogenesis. The epigenetic influences may include immunological responses, antioxidant defenses, and dietary factors, This review represents an effort to provide current research results in the aforementioned areas and an attempt to meld these events into a comprehensive overview of photocarcinogenesis. If effective prevention and intervention strategies for skin cancer are to be developed, a more thorough understanding of the disease process is imperative. (C) 1997 Elsevier Science S.A.", 
" ", 
"Several proteins that contribute to epigenetic mechanisms of gene regulation contain a characteristic motif of unknown function called the SET (Suvar3-9, Enhancer-of-zeste, Trithorax) domain. We have demonstrated that SET domains mediate highly conserved interactions with a specific family of proteins that display similarity with dual-specificity phosphatases (dsPTPases). These include myotubularin, the gene of which is mutated in a subset of patients with X-linked myotubular myopathy, and Sbf1, a newly isolated homologue of myotubularin. In contrast with myotubularin, Sbf1 lacks a functional catalytic domain which dephosphorylates phospho-tyrosine and serine-containing peptides in vitro. Competitive interference of endogenous SET domain-dsPTPase interactions by forced expression of Sbf1 induced oncogenic transformation of NIH 3T3 fibroblasts and impaired the in vitro differentiation of C2 myoblast cells. We conclude that myotubularin-type phosphatases link SET-domain containing components of the epigenetic regulatory machinery with signalling pathways involved in growth and differentiation.", 
"O-6-Methylguanine DNA methyltransferase (MGMT) repairs the mutagenic and cytotoxic O-6-alkylguanine lesions produced bg environmental carcinogens and the chemotherapeutic nitrosoureas, As such, MGMT-mediated repair of O-6-alkylguanine lesions constitutes a major form of resistance to nitrosourea chemotherapy and makes control of MGMT expression of clinical interest, The variability of expression in cell lines and tissues, along with the ease with which the MGMT phenotype reverts under various conditions, suggests that MGMT is under epigenetic control, One such epigenetic mechanism, 5-methylation of cytosines, has been linked to MGMT expression, We have used an isogenic human multiple myeloma tumor cell line model composed of an MGMT-positive parent cell line, RPMI 8226/S, and its MGMT-negative variant, termed 8226/V, to study the control of MGMT expression. The loss of MGMT activity in 8226/V was found to he due to the loss of detectable MGMT gene expression, Bisulfite sequencing of the MGMT CpG island promoter revealed large increases in the levels of CpG methylation within discrete regions of the 8226/V MGMT CpG island compared to those in 8226/S, These changes in CpG methylation are associated with local heterochromatinization of the 8226/V MGMT transcription start site and provide a likely mechanism for the loss of MGMT transcription in 8226/V.", 
"Inheritance of the active and inactive states of gene expression by individual cells is crucial for development. In fission yeast, mating-type region consists of three loci called mat1, mat2, and mat3. Transcriptionally silent mat2 and mat3 loci are separated by a 15 kb interval, designated the K-region, and serve as donors of information for transcriptionally active mat1 interconversion. In a strain carrying replacement of 7.5 kb of the K-region with the ura4 gene, we discovered that ura4 silencing and efficiency of mating-type switching were covariegated and were regulated by an epigenetic mechanism. Genetic analyses demonstrated that epigenetic states were remarkably stable not only in mitosis but also in meiosis and were linked to the mating-type region. This study indicates that different epigenetic states are heritable forms of chromatin organization at the mat region.", 
"Microdeletions of a region termed the imprinting center (IC) in chromosome 15q11-q13 have been identified in several families with Prader-Willi syndrome (PWS) or Angelman syndrome who show epigenetic inheritance for this region that is consistent with a mutation in the imprinting process. The IC controls resetting of parental imprints in 15q11-q13 during gametogenesis. We have identified a larger series of cases of familial PWS, including one case with a deletion of only 7.5 kb, that narrows the PWS critical region to <4.3 kb spanning the SNRPN gene CpG island and exon 1. Identification of a strong DNase I hypersensitive site, specific for the paternal allele, and six evolutionarily conserved (human-mouse) sequences that are potential transcription-factor binding sites is consistent with this region defining the SNRPN gene promoter. These findings suggest that promoter elements at SNRPN play a key role in the initiation of imprint switching during spermatogenesis. We also identified three patients with sporadic PWS who have an imprinting mutation (IM) and no detectable mutation in the IC. An inherited 15q11-q13 mutation or a trans-factor gene mutation are unlikely; thus, the disease in these patients may arise from a developmental or stochastic failure to switch the maternal-to-paternal imprint during parental spermatogenesis. These studies allow a better understanding of a novel mechanism of human disease, since the epigenetic effect of an IM in the parental germ line determines the phenotypic effect in the patient.", 
"The Wassilewskija strain of Arabidopsis has four genes encoding the tryptophan enzyme phosphoribosylanthranilate isomerase (PAI) located at three unlinked sites, These four PAI genes are methylated over their regions of DNA homology, When PAI copy number is reduced by deletion of two tandemly arrayed genes (MePAI1-PAI4), a mutant with fluorescent, tryptophan-deficient phenotypes results, because the two remaining methylated PAI genes (MePAI2 and MePAI3) supply insufficient PAI activity, These two methylated genes can be inherited through meiosis, even when they are segregated away from each other in crosses to a strain with unmethylated PAI genes, However, the mutant phenotypes conferred by the methylated PAI genes are unstable, and mutant plants yield occasional revertant somatic sectors and progeny. Revertant lines display coordinately reduced methylation of both PAI2 and PAI3, implying that this hypomethylation acts in a concerted manner across the genome rather than at individual sites.", 
"We report that CpG island methylation, an epigenetic modification of DNA known to correlate closely with silencing of gene transcription, appears in the oestrogen receptor (ER) gene in a subpopulation of cells which increases as a direct function of age in human colonic mucosa. This same methylation change characterizes virtually all cells in art 45 colorectal tumours examined, including the earliest stages of tumour formation. ER gene expression is diminished or absent in colorectal tumours, and introduction of an exogenous ER gene in cultured colon carcinoma cells resulted in marked growth suppression. Our data suggest that methylation associated inactivation of the ER gene in ageing cotorectal mucosa could be one of the earliest events that predispose to sporadic cotorectal tumorigenesis.", 
"A very large oxidative damage rate to DNA occurs as part of normal metabolism. In each rat cell the steady-state level is estimated to be about 10(6) oxidative adducts and about 10(5) new adducts are formed daily. It is argued that this endogenous DNA damage is a major contributor to aging and the degenerative diseases of aging, such as cancer. The oxidative damage rate in mammalian species with a high metabolic rate, short life span, and high age-specific cancer rate is much higher than the rate in humans, a long-lived creature with a lower metabolic rate and a lower age-specific cancer rate. It is argued that deficiency of micronutrients, such as dietary antioxidants or folate, is a major contributor to human cancer and degenerative diseases. Understanding the role of mitogenesis in mutagenesis is critical for clarifying the mechanisms of carcinogenesis and interpreting high-dose animal cancer tests. High-dose animal cancer tests have been done mainly on synthetic industrial chemicals, yet almost all of the chemicals humans are exposed to are natural. About half of natural chemicals tested in high-dose animal cancer tests are rodent carcinogens, a finding that is consistent with the view that high-dose tests frequently increase mitogenesis rates. Animals have numerous defenses against toxins that make them very well buffered against low doses of almost all toxins, whether synthetic or natural.", 
"The expression of the H19 gene is governed by parental imprinting in mammals. H19, an unusual gene encoding an RNA with no known function, is exclusively expressed from the maternal chromosome. In mouse, it lies 90 kb downstream from the Igf2 gene, which encodes a fetal-specific growth factor, insulin-like growth factor II, and is expressed primarily from the paternally inherited chromosome. In this report we have utilized interspecific hybrid mice to identify male-specific DNA methylation of a 7- to 9-kb domain surrounding the H19 gene and its promoter. This allele-specific methylation could function as a mark to suppress transcription of the H19 paternal allele. Consistent with this proposal, the H19 promoter displayed an open chromatin conformation only on the relatively unmethylated active maternal allele. In contrast, a cell type-specific enhancer that lies outside the methylation domain is hypersensitive to restriction enzyme digestion in nuclei on both maternal and paternal chromosomes. That the allele-specific methylation domain, coupled to the two H19 enhancers, contains all the information necessary for its imprinting was tested by examining two transgenic lines containing an internally deleted H19 transgene. Both displayed paternal-specific methylation of the transgene and maternal-specific expression. Although neither line has been tested in an inbred genetic background, and therefore the action of complex modifiers cannot be formally excluded, the result suggests that the sequences necessary for the imprinting of H19 have been identified.", 
"The insulin-like growth factor-II (IGF2) and H19 genes are imprinted in mouse and human, with expression of the paternal IGF2 and maternal H19 alleles. IGF2 undergoes loss of imprinting (LOI) in most Wilms' tumours (WT). We now show that: (i) LOI of IGF2 is associated with a 80-fold down regulation of H19 expression; (ii) these changes are associated with alterations in parental-origin-specific, tissue-independent sites of DNA methylation in the H19 promoter; and (iii) loss of heterozygosity is also associated with loss of H19 expression. Thus, imprinting of a large domain of the maternal chromosome results in a reversal to a paternal epigenotype. These data also suggest an epigenetic mechanism for inactivation of H19 as a tumour suppressor gene.", 
"The recent discovery of widely distributed targeting determinants, which govern the polarized cell-surface distribution of plasma membrane proteins in epithelial cells, has significantly changed our view of how polarized cells generate functionally distinct membrane domains. Together with the surprising finding that the same determinants are recognized on both the biosynthetic and the endocytic pathways, it now appears likely that a common epigenetic code may exist that controls molecular sorting of membrane proteins in a wide variety of polarized, and perhaps even non-polarized, cell types.", 
"Inactivation of the retinoblastoma gene appears to have a fundamental role in the genesis of retinoblastoma, osteosarcoma, and other malignant tumors. The gene is generally inactivated because of loss-of-function mutations, although epigenetic phenomena, such as hypermethylation of the promoter region, could possibly have the same effect. We investigated the methylation pattern at the 5' end of the retinoblastoma gene, including its promoter region and exon 1, in DNA purified from 56 primary retinoblastomas. We found five tumors with evidence for hypermethylation, all from unilateral, simplex patients. No methylation abnormalities were detected in DNA purified from the leukocytes from these patients. It is interesting that in one of these tumors the hypermethylation was confined to one allele. There were no mutations in a 1,306-bp sequence including the hypermethylated region that might account for the allele-specific hypermethylation. We believe that the hypermethylation of the retinoblastoma gene that we found in these tumors corresponds to the allelic inactivation of the gene, and we speculate that erroneous hypermethylation without alteration of nucleotide sequence occasionally plays a role in the genesis of this cancer. If this is true, then retinoblastomas with hypermethylation might be treatable with chemotherapeutic agents that interfere with methylation of DNA.", 
"Becker muscular dystrophy (BMD) often results from in-frame mutations of the dystrophin gene that allow production of an altered but partially functional protein. To address potential structure-function relationships for the various domains of dystrophin, we examined both the dystrophin gene and protein in 68 patients with abnormal dystrophin. Eighty-six percent of BMD patients with dystrophin of altered size have deletions or duplications, and the observed sizes of dystrophin fit well with predictions based on DNA data. Deletions within the amino-terminal domain I tended to result in low levels of dystrophin and a more severe phenotype. The phenotypes of patients with deletions or duplications in the central rod domain were more variable. This region can be divided into three portions based on differences in clinical presentations of patients. Deletions around exons 4553 were most common and generally caused typical BMD; however, phenotypic variability among patients with similar mutations suggests that epigenetic and/or environmental factors play an important role in determining the clinical progression. In contrast, deletions or duplications in the proximal portion of this domain tended to cause severe cramps and myalgia. Finally, loss of the middle of this region probably causes a very mild phenotype, as only one such patient was found and his only symptom was elevated serum creatine phosphokinase levels.", 
"Massive cell migration, proliferation, phenotypic differentiation, and enhanced biosynthetic activities characterize the sites of wound healing and fibrosis. Regulation of cellular functions by extracellular matrix, which consists of a dynamic assemblage of a variety of interacting molecules capable of reorganization in response to endogenous and exogenous stimuli, represents a fundamental epigenetic mechanism regulating cellular behavior and phenotype. Interactions of the individual components of extracellular matrix with specific cell surface molecules, integrin receptors, and proteoglycans initiate a cascade of signal transduction leading to varied short-term or persistent cellular responses. Extracellular matrix also serves as an important reservoir of cytokines and growth factors, thus modulating the action of a host of potent biological response modifiers by their selective, local accumulation and release. Currently known mechanisms by which extracellular matrix modulates different facets of the process of tissue remodeling after injury, which culminate either in normal wound repair or fibrosis, are discussed.", 
"To test the potential role of H19 as a tumour suppressor gene we have examined its expression and DNA methylation in Wilms' tumours (WTs). In most WTs (18/25), H19 RNA was reduced at least 20-fold from fetal kidney levels. Of the expression-negative tumours ten retained 11p15.5 heterozygosity: in nine of these, H19 DNA was biallelically hypermethylated and in two cases hypermethylation locally restricted to H19 sequences was also present in the non-neoplastic kidney parenchyma. IGF2 mRNA was expressed in most but not all WTs and expression patterns were consistent with IGF2/H19 enhancer competition without obligate inverse coupling. These observations implicate genetic and epigenetic inactivation of H19 in Wilms' tumorigenesis.", 
"Segmentation genes provide the signals for the activation and regulation of homeotic genes in Drosophila but cannot maintain the resulting pattern of expression because their activity ceases halfway through embryogenesis. Maintenance of the pattern is due to the Polycomb group of genes (Pc-G) and the trithorax group of genes (trx-G), responsible for the persistence of the active or repressed state of homeotic genes. We have identified a regulatory element in the Ubx gene that responds to Pc-G and trx-G genes. Transposons carrying this element create new binding sites for Pc-G products in the polytene chromosomes. This Pc-G maintenance element (PRE), establishes a repressive complex that keeps enhancers repressed in cells in which they were originally repressed and maintains this state through many cell divisions. The trx-G products stimulate the expression of enhancers in cells in which they were originally active. This mechanism is responsible for the correct regulation of imaginal disc enhancers, which lack themselves antero-posterior positional information. The PRE also causes severe variegation of the mini-white gene present in the transposon, a phenomenon very similar to heterochromatic position-effect variegation. The significance of this mechanism for homeotic gene regulation is discussed.", 
"Chromatin structure at Schizosaccharomyces pombe centromeres is unusual. The insertion of the ura4 gene within these centromeres resulted in genetically identical cells mosaic for its expression. Placement of the ade6 gene within cen1 or cen3 resulted in red-white sectored colonies, demonstrating the instability of gene expression. The occurrence of pink colonies implied that intermediate levels of repression were established. Repression of both genes within centromeres was temperature sensitive. The chromatin structure of the ura4 gene at centromeres was altered, suggesting that the unusual chromatin encroaches into the gene and inhibits normal expression. These repressive effects at S. pombe centromeres resemble the classical phenomenon of position effect variegation imposed by Drosophila heterochromatin on nearby genes. However, since the epigenetic states can be set at intermediate levels of expression, a purely euchromatin-heterochromatin dichotomy does not apply. A model for the epigenetic regulation of genes placed within S. pombe centromeres is presented.", 
"The mouse insulin-like growth factor II (Igf2) gene, which is located on distal chromosome 7 (Chr7), has been shown previously to undergo tissue-specific parental imprinting. This imprinting results in expression of Igf2 from the paternally inherited chromosome and repression of the maternally inherited allele in most tissues of the developing embryo. We are using embryos with the maternal duplication and paternal deficiency of distal Chr7 to characterize the mechanism that underlies repression of the maternal allele. We show that the chromatin of the 5' region of the repressed Igf2 allele is potentially active for transcription rather than heterochromatic. In particular, a CpG island that comprises one of the two strong promoters is unmethylated at both parental alleles, and DNase I hypersensitive sites in and around the strong promoters are consistently present on both parental chromosomes. In agreement with the chromatin state, primary transcripts from the maternal Igf2 allele have been detected at low but significant levels. These findings differ from observations in other instances of imprinting, namely, X-chromosome inactivation and transgene imprinting in mice. Although no parent-specific differences were detected in either DNA methylation or sensitivity to nucleases at these promoters, we have observed parental methylation differences in a region several kilobases upstream of the first exon. The differential activity of the parental Igf2 alleles could be achieved through epigenetic modifications situated outside the promoters or by subtle and yet unidentified modifications at the promoters.", 
"The Insulin-like growth factor 2 (Igf2) and H19 genes are reciprocally imprinted and closely linked. Igf2 encodes a fetal growth-factor and is predominantly expressed from the paternal allele, while H19 is expressed from the maternal allele and encodes a transcript which may downregulate cellular proliferation. One of the epigenetic modifications thought to be involved in parental imprinting is DNA methylation. Here we analyse methylation in two regions of the Igf2 gene, one approx. 3 kb upstream of the gene and one in the 3' part of the gene. Both regions are more methylated on the expressed paternal chromosome. Genomic sequencing of individual chromosomes in the first region shows this parent-specific methylation to be highly mosaic; interestingly, individual sperm chromosomes carry different methylation patterns into the egg. In the more 3' region, which is fully methylated in sperm, the level of methylation on the paternal allele is highly tissue-specific and is correlated with expression of the gene in fetal tissues. Hence, the paternal allele is highly methylated in fetal liver (high expression) but is undermethylated in fetal brain (virtually no expression). Adult choroid plexus, a brain tissue in which Igf2 is expressed from both alleles and H19 is not expressed, represents an apparent loss of imprinting. Here, both Igf2 and H19 adopt a paternal type methylation pattern on both parental chromosomes. Analysis of early-passage androgenetic and parthenogenetic embryonic stem (ES) cells shows that the methylation patterns of Igf2 and H19 on maternal and paternal chromosomes are very similar. Androgenetic and parthenogenetic teratomas derived from these ES cells show the appropriate paternal and maternal patterns, respectively, of allelic methylation in both genes. Our results suggest that allelic methylation patterns in Igf2 and H19 arise early in embryogenesis and change progressively during development. Some of these developmental changes are apparently under tissue-specific control.", 
"In several plant systems expression of structurally intact genes may be silenced epigenetically when a transgenic construct increases the copy number of DNA sequences. Here we report epigenetic silencing in Arabidopsis lines containing transgenic inserts of defined genetic structure, all at the same genomic locus. These comprise an allelic series that includes a single copy of the primary insert, which carries repeated drug resistance transgenes, and a set of its derivatives, which as a result of recombination within the insert carry different numbers and alleles of resistance genes. Although the drug resistance genes remained intact, both the primary and some recombinant lines nevertheless segregated many progeny that were partly or fully drug-sensitive because of silencing. As in other systems silencing was reversible, and correlated with decreased steady-state mRNA and increased DNA methylation. Each different number and combination of genes, on the same or different (i.e., homologous) chromosomes, conditioned its own idiosyncratic segregation pattern. Strikingly, lines with a single gene segregated only a few slightly drug-sensitive progeny whereas multi-gene lines segregated many highly sensitive progeny, indicating dependence of silencing at this locus on repeated sequences. This argues strongly against explanations based on antisense RNA, but is consistent with explanations based on ectopic DNA pairing. One possibility is that silencing reflects the interaction of paired homologous DNA with flanking heterologous DNA, which induces condensation of chromatin into a non-transcribable state.", 
"Modifiers of position-effect-variegation in Drosophila encode proteins that are thought to modify chromatin, rendering it heritably changed in its expressibility. In an attempt to identify similar modifier genes in other species we have utilized a known sequence homology, termed chromo box, between a suppressor of position-effect-variegation, Heterochromatin protein 1 (HP1), and a repressor of homeotic genes, Polycomb (Pc). A PCR generated probe encompassing the HP1 chromo box was used to clone full-length murine cDNAs that contain conserved chromo box motifs. Sequence comparisons, in situ hybridization experiments, and RNA Northern blot analysis suggest that the murine and human sequences presented in this report are homologues of the Drosophila HP1 gene. Chromo box sequences can also be detected in other animal species, and in plants, predicting a strongly conserved structural role for the peptide encoded by this sequence. We propose that epigenetic (yet heritable) changes in gene expressibility, characteristic of chromosomal imprinting phenomena, can largely be explained by the action of such modifier genes. The evolutionary conservation of the chromo box motif now enables the isolation and study of putative modifier genes in those animal and plant species where chromosomal imprinting has been described.", 
" ", 
" ", 
"The molecular mechanisms introducing epigenetic modifications that lead to differential silencing of some autosomal alleles depending on their parental legacy are still largely unknown, but recent results from studies of endogenously imprinted genes and particular transgenes make DNA methylation a strong candidate. At the same time, these results have raised new questions about the details of the imprinting process.", 
"Previous work has shown that two homologous, unlinked transgene loci can interact in plant nuclei, leading to non-reciprocal trans-inactivation and methylation of genes at one locus. Here, we report the structure and methylation of different transgene loci that contain the same construct but are variably able to inactivate and methylate a partially homologous, unlinked target locus. Silencing loci comprised multiple, methylated copies of the transgene construct, whereas a non-silencing locus contained a single, unmethylated copy. The correspondence between strength of silencing activity and copy number/degree of methylation was further demonstrated by producing novel alleles of a strong silencing locus: reducing the transgene copy number and methylation within this silencing locus decreased its ability to inactivate the target locus. The strong silencing locus, which was located close to a telomere, trans-inactivated various structural variants of the original target construct, regardless of their location in the genome. This suggests that the silencing locus can scan the entire genome for homologous regions, a process possibly aided by its telomeric location. Our data support the idea that epistatic trans-inactivation of unlinked, homologous transgenes in plants results from a pre-existing epigenetic difference between transgene loci, which is subsequently equalized by ''epigene conversion'' involving DNA-DNA pairing.", 
" ", 
"Major epigenetic modifications apparently occur during early development in the mouse. The factors that induce such modifications are complex and may involve the various components of a zygote. We have started to explore whether changes in the nucleocytoplasmic composition brought about by micromanipulation can induce phenotypic effects through epigenetic modifications. Nucleocytoplasmic hybrids were therefore prepared by transplanting a female pronucleus into a recipient egg from a different genotype. As a result, the maternal genome was of a different genetic background as compared with the egg cytoplasm. Specifically, experimental zygotes had cytoplasm from the inbred strain C57BL/6, a maternal genome from DBA/2, and a paternal genome from C57BL/6 (termed BDB hybrids). The mirror-image combination, termed DBD, was also made. The reconstituted zygotes were transferred to recipients and allowed to develop to term. Mice born from manipulated zygotes showed transcriptional repression and DNA methylation of major urinary protein genes in their liver, as well as growth deficiency resulting in reduced adult body weight. No altered phenotype was observed in controls in which the maternal pronucleus was simply transplanted back into another zygote of the same genetic background. These results clearly demonstrate phenotypic as well as molecular effects on DNA methylation and expression of at least one gene. Phenotype was therefore no longer predicted by genotype as a result of epigenetic modifications in experimental embryos. What precisely triggers the phenotypic and epigenetic changes is unknown, but presumably, nucleocytoplasmic interactions in hybrid zygotes may be partly responsible.", 
"The DNA of eukaryotic cells is organized in a complex with proteins, either as interphase chromatin or mitotic chromosomes. Nucleosomes, the structural subunits of chromatin, have long been considered as static structures, incompatible with processes occurring in chromatin. During the past few years it has become evident that the histone part of the nucleosome has important regulatory functions. Some of these functions are mediated by the N-terminal core histone domains which contain sites for posttranslational modifications, among them lysine residues for reversible acetylation. Recent results indicate that acetylation and deacetylation of N-terminal lysines of nucleosomal core histones represent a means of molecular communication between chromatin and the cellular signal transduction network, resulting in heritable epigenetic information. Data on enzymes involved in acetylation and the pattern of acetylated lysine sites on chromosomes, as well as genetic data on yeast transcriptional repression, suggest that acetylation may lead to structural transitions as well as specific signalling within distinct chromatin domains.", 
" ", 
"Messenger RNA and methylation levels of four imprinted genes, H19, Igf2r, Igf-2 and Snrpn were examined by northern and Southern blotting in mouse parthenogenetic, androgenetic and normal or wild-type embryonic stem cell lines during their differentiation in vitro as embryoid bodies. Zn most instances, mRNA levels in parthenogenetic and androgenetic embryoid bodies differed from wild type as expected from previously determined patterns of monoallelic expression in midgestation embryos and at later stages of development. These findings implicate aberrant mRNA levels of these genes in the abnormal development of parthenogenetic and androgenetic embryos and chimeras. Whereas complete silence of one of the parental alleles has previously been observed in vivo, we detected some mRNA in the corresponding embryonic stem cell line. This 'leakage' phenomenon could be explained by partial erasure, bypass or override of imprints, or could represent the actual activity status at very early stages of development. The mRNA levels of H19, Igf2r and Igf-2 and the degree of methylation at specific associated sequences were correlated according to previous studies in embryos, and thereby are consistent with suggestions that the methylation might play a role in controlling transcription of these genes. Paternal-specific methylation of the H19 promoter region is absent in sperm, yet we observed its presence in undifferentiated androgenetic embryonic stem cells, or before the potential expression phase of this gene in embryoid bodies. As such methylation is likely to invoke a repressive effect, this finding raises the possibility that it is part of the imprinting mechanism of H19, taking the form of a secondary imprint or postfertilization epigenetic modification necessary for repression of the paternal allele.", 
"The SNRPN gene encodes a small nuclear ribonucleoprotein subunit, SmN, thought to be involved in splicing of pre-mRNA. A closely related protein, SmB/B', is constitutively expressed in all tissues except the brain, where SmN is predominantly expressed. The mouse homolog of the SNRPN gene has been shown to be functionally imprinted in mouse brain, being expressed only from the paternally derived chromosome. SNRPN has been mapped to human chromosome 15q11-q13 within the shortest region of deletion overlap for the Prader-Willi syndrome. We have now demonstrated functional imprinting of the human SNRPN gene using reverse transcription followed by the polymerase chain reaction (RT-PCR). No expression was observed in cultured skin fibroblasts of Prader-Willi patients, but was found in all Angelman patients and normal controls examined. We have also demonstrated a parent-specific DNA methylation imprint within intron 5 of the SNRPN gene, which suggests an epigenetic mechanism by which parent-specific expression of this gene might be inherited. Our findings indicate that SNRPN is expressed only from the paternally derived chromosome 15 in humans and therefore may fullfill one major criterion for being involved in the pathogenesis of the Prader-Willi syndrome.", 
"Development in mammals is influenced by genome imprinting which results in differences in the expression of some homologous maternal and paternal alleles. This process, initiated in the germline, can continue following fertilization with interactions between oocyte cytoplasmic factors and the parental genomes involving modifier genes. Further epigenetic modifications may follow to render the 'imprints' heritable through subsequent cell divisions during development. Imprinting of genes can be critical for their dosage affecting embryonic growth, cell proliferation and differentiation. The cumulative effects of all the imprinted genes are observed in androgenones (AG) and parthenogenones (PG), which reveal complementary phenotypes with respect to embryonic and extraembryonic tissues. The presence of PG cells in chimeras causes growth retardation, while that of AG cells enhanced growth. AG cells apparently have a higher cell proliferation rate and, unlike PG cells, are less prone to selective elimination. However, the PG germ cells are exempt from cell selection. In chimeras, PG cells are more likely to be found in ectodermal derivatives such as epidermis and brain in contrast to AG cells which make pronounced contributions to many mesodermal derivatives such as muscle, kidney, dermis and skeleton. The presence of androgenetic cells in chimeras also results in the disproportionate elongation of the anterior-posterior axis and sometimes in the abnormal development of skeletal elements along the axis. Genetic studies highlight the influence of subsets of imprinted genes, and identify those that are critical for development.", 
"Zea mays transformants produced by particle bombardment of embryogenic suspension culture cells of the genotype A188 x B73 and selected on kanamycin or bialaphos were characterized with respect to transgene integration, expression, and inheritance. Selection on bialaphos, mediated by the bar or par genes, was more efficient than selection on kanamycin, mediated by the nptII gene. Most transformants contained multicopy, single locus, transgene insertion events. A transgene expression cassette was more likely to be rearranged if expression of that gene was not selected for during callus growth. Not all plants regenerated from calli representing single transformation events expressed the transgenes, and a nonselectable gene (uidA) was expressed in fewer plants than was the selectable transgene. Mendelian inheritance of transgenes consistent with transgene insertion at a single locus was observed for approximately two thirds of the transformants assessed. Transgene expression was typically, but not always, predictable in progeny plants - transgene silencing, as well as poor transgene transmission to progeny, was observed in some plant lines in which the parent plants had expressed the transgene.", 
"Although Angelman (AS) and Prader-Willi (PWS) syndromes are human genetic disorders with distinctly different developmental and neurobehavioural phenotypes, they both have abnormalities in inheritance of chromosome 15q11-q13. Whether AS or PWS arises depends on the parental origin of a deletion or uniparental disomy (the inheritance of 2 copies of a genetic locus from only one parent) for 15q11-q13. Normal development requires a genetic contribution for this genetic region from both a male and a female parent. The dependence on parental origin implies that genes in human 15q11-q13 have distinct functions depending upon epigenetic, parent-of-origin differences, known as genomic imprinting. Here, I review the role of uniparental disomy and genomic imprinting in the pathogenesis of AS and PWS, and briefly discuss phenotype-genotype correlations using candidate genes and mouse models, in particular for hypopigmentation.", 
"Because development is epigenetic, diverse aspects of morphology are integrated during ontogeny. Using the method of thin-plate splines, and the decomposition of these splines by their principal warps, we examine the ontogeny of integrated features of skull growth of the cotton rat, Sigmodon fulviventer as observed in landmark locations in the ventral view. Postnatal growth of the skull in Sigmodon is not adequately described by the familiar contrast between relatively rapid facial elongation and slow, precocial growth of the cranial base. No developmental units corresponding to facial skull and cranial base emerge from analysis of geometric shape change. Rather, skull growth is both more integrated and more complex, exhibiting both skull-wide integration and locally individualized regions. Like skull shape, integration has an ontogeny; different regions of the skull can be partitioned into developmentally individualized parts in different ways at different ages. The effective count of individualized parts decreases substantially before weaning occurs, suggesting that the integration required by the functionally demanding activity of chewing gradually develops before the functional transition occurs. Our description of skull growth and integration does not depend upon arbitrary a priori choices about what to measure; rather, we base our decomposition of the whole into parts upon results of the data analysis. Our approach complicates the study of heterochrony, but, because it expresses the spatiotemporal organization of ontogeny, it enables the study of heterotopy.", 
"A novel epigenetic mechanism that can affect minichromosome centromere function in vivo has been identified in S. pombe. This epigenetic system can result in the conversion of a nonfunctional centromere to a functional one without changes in the content, structural arrangement, or chemical modification state of the minichromosomal DNA. The conversion from a centromere-inactive to an active state, which is evident with minichromosomes carrying abbreviated centromeric DNA constructions, occurs with a relatively high frequency during mitotic cell divisions and readily provides an in vivo essay for proper centromere formation. The centromere-targeted epigenetic system supports a model for centromere function that involves specific de novo folding of centromeric components into a higher order chromatin structure.", 
"During development, patterns of differential gene expression, defining determined states of cells, need to be maintained over many cell generations. In Drosophila, genetic and molecular analyses led to the discovery of a set of proteins which seem to exert such a memory function by using epigenetic mechanisms. Recent experiments demonstrate that, in particular, the heritable inactivation of regulatory genes relies on stable changes in the higher-order constitution of chromatin.", 
"The ability of chemicals with tumor-promoting or tumor-inhibiting activity to modulate gap junctional intercellular communication is reviewed. The two most extensively used types of assays for screening tests are (1) metabolic cooperation assays involving exchange between cells of precursors of nucleic acid synthesis and (2) dye-transfer assays that measure exchange of fluorescent dye from loaded cells to adjacent cells. About 300 substances of different biological activities have been studied using various assays. For tumor promoters/epigenetic carcinogens, metabolic cooperation assays have a sensitivity of 62% and dye-transfer assays 60%. Thirty percent of DNA-reactive carcinogens also possess the ability to uncouple cells. The complete estimation of the predictive power of these assays could not be made because the majority of the substances studied for intercellular communication effects in vitro have not yet been studied for promoting activity in vivo. Both metabolic cooperation assays and dye transfer assays respond well to the following classes of substances: phorbol esters, organochlorine pesticides, polybrominated biphenyls, promoters for urinary bladder, some biological toxins, peroxisome proliferators, and some complex mixtures. Results of in vitro assays for such tumor promoters/nongenotoxic carcinogens, such as some bile acids, some peroxides, alkanes, some hormones, mineral dusts, ascorbic acid, okadaic acid, and benz(e)pyrene, do not correlate with the data of in vivo two-stage or complete carcinogenesis. Enhancement of intercellular communication was found for 18 chemicals. Among these, cAMP, retinoids, and carotenoids have demonstrated inhibition of carcinogenesis. We examine a number of factors that are important for routine screening, including the requirement for biotransformation for some agents to exert effects on gap junctions. We also discuss the mechanisms of tumor promoter and tumor inhibitor effects on gap junctional permeability, including influences of protein kinase activation, changes in proton and Ca2+ intracellular concentrations, and effects of oxy radical production.", 
"Ascobolus immersus artificial gene repeats were shown previously to be subject premeiotically to both cytosine methylation and inactivation. We studied sexual progenies of strains harbouring two wild type copies of the endogenous met2 gene lying either in tandem array or at ectopic unlinked positions, by (i) investigating the methylation status, (ii) searching for mutations and (iii) analysing the inheritance of inactivation both in mitotic and sexual offspring. 100% of the 'tandem' progeny and 64% of the 'ectopic' progeny had methylated repeats and displayed gene inactivation. Similar methylation patterns involving all or most of the cytosine residues within the repeats were observed in both arrangements. The inactivated met2 copies were totally devoid of mutation, as deduced from: (i) extensive restriction site analysis and DNA sequencing; (ii) the finding that all the Met- derivatives tested reverted to prototrophy in selective conditions; and (iii) the finding that an inactivated copy of met2 stripped of its methylation through amplification in Escherichia coli regained activity when reintroduced in A. immersus. In the absence of selection, gene silencing and methylation were faithfully maintained through mitotic divisions and through five successive sexual cycles. Altogether, these data show the epimutational nature of this methylation induced premeiotically (MIP) process.", 
"Transposable elements from the Robertson's Mutator family are highly active insertional mutagens in maize. However, mutations caused by the insertion of responder (non-autonomous) elements frequently depend on the presence of active regulator (autonomous) elements for their phenotypic effects. The hcf106::Mu1 mutation has been previously shown to depend on Mu activity in this way. The dominant Lesion-mimic 28 mutation also requires Mu activity for its phenotypic effects. We have used double mutants to show that the loss of Mu activity results in the coordinate suppression of both mutant phenotypes. This loss can occur somatically resulting in large clones of cells that have a wild-type phenotype. Autonomous and non-autonomous Mutator elements within these clones are insensitive to digestion with methylation-sensitive enzymes, suggesting extensive methylation of CG and non-CC cytosine residues. Our data are consistent with the sectors being caused by the cycling of MuDR regulatory elements between active and inactive phases. The pattern of sectors suggests that they are clonal and that they are derived from the apical cells of the vegetative shoot meristem. We propose that these cells are more likely to undergo epigenetic loss of Mu activity because of their longer cell division cycle during shoot growth. Coordinate suppression of unlinked mutations can be used to perform mosaic analysis in maize.", 
"The neural crest is a fascinating structure of the vertebrate embryo; its ontogeny includes a transient period during which its component cells undergo an epithelio-mesenchymal transition and become migratory. This phase was shown recently to be controlled by the 'Slug' gene which belongs to the 'Snail' family of Drosophila transcription factors. After homing to specific sites in the embryo, the crest-derived cells produce a large variety of phenotypes. Recent advances have shown that during migration most crest cells exhibit various degrees of pluripotentiality, some being already committed to a single and definite fate. Moreover, several lines of evidence point to the existence of totipotent stem cells in the neural crest, the progeny of which become progressively diversified through a combination of intrinsic and extrinsic influences. The latter have been documented by the disruption of several neurotrophin genes, which results in severe deficiencies of selected subsets of neural crest derivatives. The neural crest has also been shown to play an important role in the development of the vertebrate head and hypobranchial region. The genetic control of this process depends on the. activity of developmental genes, among which the vertebrate Hox genes are essential, particularly at the rhombencephalic level.", 
"The ability of simian virus 40-encoded large T antigen to disrupt the growth control of a variety of cell types is related to its ability to interfere with certain cellular proteins, such as p53 and the retinoblastoma susceptibility gene product (pRB). We have used wild-type and mutant forms of T antigen in transgenic mice to dissect the roles of pRB, p53, and other cellular proteins in tumorigenesis of different cell types. In this study, using a cell-specific promoter to target expression specifically to brain epithelium (the choroid plexus) and to B and T lymphoid cells, we characterize the tumorigenic capacity of a T-antigen fragment that comprises only the amino-terminal 121 residues. This fragment (dl1137) retains the ability to interact with pRB and p107 but lacks the p53-binding domain. While loss of the p53-binding region results in loss of the capacity to induce lymphoid abnormalities, dl1137 retains the ability to induce choroid plexus tumors that are histologically indistinguishable from those induced by wild-type T antigen. Tumors induced by dl1137 develop much more slowly, however, reaching an end point at around 8 months of age rather than at 1 to 2 months. Analysis of tumor progression indicates that tumor induction by dl1137 does not require secondary genetic or epigenetic events. Rather, the tumor growth rate is significantly slowed, indicating that the T-antigen C-terminal region contributes to tumor progression in this cell type. In contrast, the pRB-binding region appears essential for tumorigenesis as mutation of residue 107, known to disrupt pRB and p107 binding to wild-type T antigen, abolishes the ability of the dl1137 protein to induce growth abnormalities in the brain.", 
"In this study, we used the ADE2 gene in a colony color assay to monitor transcription from the normally silent HMR mating-type locus in Saccharomyces cerevisiae. This sensitive assay reveals that some previously identified cis- and trans-acting mutations destabilize silencing, causing genetically identical cells to switch between repressed and derepressed transcriptional states. Deletion of the autonomously replicating sequence (ARS) consensus element at the HMR-E silencer or mutation of the silencer binding protein RAP1 (rap1s) results in the presence of large sectors within individual colonies of both repressed (Ade-, pink) and derepressed (Ade+, white) cells. These results suggest that both the ARS consensus element and the RA-P1 protein play a role in the establishment of repression at HMR. In diploid cells, the two copies of HMR appear to behave identically, suggesting that the switching event, though apparently stochastic, reflects some property of the cell rather than a specific event at each HMR locus. In the ADE2 assay system, silencing depends completely upon the function of the SIR genes, known trans-acting regulators of the silent loci, and is sensitive to the gene dosage of two SIR genes, SIR1 and SIR4. Using the ADE2 colony color assay in a genetic screen for suppressors of rap1s, silencer ARS element deletion double mutants, we have identified a large number of genes that may affect the establishment of repression at the HMR silent mating-type locus.", 
"We analysed de novo DNA methylation occurring in plants obtained from the transgenic petunia line R101-17. This line contains one copy of the maize Al gene that leads to the production of brick-red pelargonidin pigment in the flowers. Due to its integration into an unmethylated genomic region the A1 transgene is hypomethylated and transcriptionally active. Several epigenetic variants of line 17 were selected that exhibit characteristic and somatically stable pigmentation patterns, displaying fully coloured, marbled or colourless flowers. Analysis of the DNA methylation patterns revealed that the decrease in pigmentation among the epigenetic variants was correlated with an increase in methylation, specifically of the transgene DNA. No change in methylation of the hypomethylated integration region could be detected. A similar increase in methylation, specifically in the transgene region, was also observed among progeny of R101-17del, a deletion derivative of R101-17 that no longer produces pelargonidin pigments due to a deletion in the Al coding region. Again de novo methylation is specifically directed to the transgene, while the hypomethylated character of neighbouring regions is not affected. Possible mechanisms for transgene-specific methylation and its consequences for long-term use of transgenic material are discussed.", 
"Plant cells growing in an artificial culture environment make numerous genetic mistakes. These alterations are manifested as increased frequencies of single-gene mutations, chromosome breakages, transposable element activations, quantitative trait variations, and modifications of normal DNA methylation patterns. Evidence is presented that indicates a high frequency of DNA hypomethylation as the result of the tissue culture process. Fifteen percent of the methylation changes appear to have been homozygous in the original regenerated plants. A hypothesis is advanced that relates DNA methylation to the variety of genetic alterations found among maize tissue culture regenerants and their progenies. The epigenetic nature of DNA methylation raises questions concerning the stability of tissue culture-induced changes in self-pollinations and crosses.", 
"In this essay review I describe the relationship between plant organization, variation, and evolution. The hypothetical optimal design of an organism living in a given environment must be specified to test whether evolution is adaptive. In a variable environment this design should include a system for plasticity. Plasticity in plants is made possible by modular growth. In modular growth new parts can constantly be added to a body, resulting in a population-like structure of the organism. The developmental basis for modular growth is an open-ended ontogeny in which the formation of organs is not controlled by patterns of cell divisions and migrations and where there is no separation into germ-line and soma. Epigenetic pattern formation, late differentiation, and loose integration of the individual arising from a zygote (genet) are characteristic for plants. Because the phenotype is the result of an interaction between genotype and environment, the contributions of the two cannot be separated. Nevertheless, with appropriate experimental procedures it is possible to separate the variation among phenotypes into variation among genotypes, variation among environments, and covariation of genotypes and environments. Several genotypes must be grown in several environments. If the environments can be put on a scale, as in gradient experiments, reaction norms of genotypes may be quantified. Local specialization of genotypes in a heterogeneous environment may be recognized by transplant experiments. New results from both types of experiments indicate that the 'general-purpose genotype' is more common than originally thought and suggest that phenotypic plasticity in plants has relatively low costs. However, the critical experiments to measure these costs have not yet been published. The genetic analysis of phenotypic variation and the use of phenotypic characters for reconstructing phylogenies is hampered by the particular plant features mentioned above. Environment-induced phenotypic effects can be persistent and can be transmitted to clonal or even sexual progeny. Gene flow among taxa via sexual and possibly other mechanisms together with the loose integration of the individual make it difficult to recognize phylogenies for systematic groups in plants. Some of these problems are illustrated with species from the genera Solidago and Carex.", 
"Mating-type genes resident in the silent cassette HML at the left arm of chromosome III are repressed by the action of four SIR gene products, mediated independently through two cis-acting sites, termed the E and I silencers. We have found that in the absence of the I silencer, deletion of any one of three distinct elements within E yields partial derepression of the mating-type genes resident at HML, whereas deletion of any two yields full derepression. These elements correspond to a binding site for the abundant DNA-binding protein RAP1, an autonomous replicating sequence (ARS), and an as yet undistinguished region. From detailed deletion analysis of the E site we conclude that the ARS element contributes to silencer function in a capacity distinct from its role as an initiator of DNA replication. In addition, we find that strains deleted for any one of these elements comprise two genetically identical but phenotypically distinct types of cells: Those with HML apparently fully derepressed, and those with HML apparently completely repressed. These results reinforce the notion that epigenetic inheritance is an intrinsic characteristic of silencer action.", 
"Two instances of genetic transmission of spontaneous epimutation of the maize P-rr gene were identified. Transmission gave rise to two similar, moderately stable alleles, designated P-pr-1 and P-pr-2, that exhibited Mendelian behavior. Both isolates of P-pr conditioned a variable and variegated phenotype, unlike the uniform pigmentation conditioned by P-rr. Extensive genomic analysis failed to reveal insertions, deletions or restriction site polymorphisms between the new allele and its progenitor. However, methylation of the P gene was increased in P-pr relative to P-rr, and was greatly reduced (though not lost) in a revertant to uniform pigmentation. Variability in pigmentation conditioned by P-pr correlated with variability in transcript levels of the P gene, and both correlated inversely with variability in its methylation. Part of the variability in methylation could be accounted for by a developmental decrease in methylation in all tissues of plants carrying P-pr. We hypothesize that the variegated phenotype results from a general epigenetic pathway which causes a progressive decrease in methylation and increase in expression potential of the P gene as a function of cell divisions in each meristem of the plant. This renders all tissues chimeric for a functional gene; chimerism is visualized as variegation only in pericarp due to the tissue specificity of P gene expression. Therefore, this allele that originates from epimutation may exemplify an epigenetic mechanism for variegation in maize.", 
"Previous work has shown that two unlinked, partially homologous transgene loci can interact in plant nuclei, leading to reversible methylation and inactivation of one transgene locus in the presence of the second. To study whether the chromosomal location of a transgene influences its susceptibility to trans-inactivation, we retransformed four transgenic lines, which contained the same construct (H) integrated in different chromosomal locations, with a second, partially homologous construct (K). At least 50 double transformants (DTs) were regenerated from each single transformant (ST) and screened for inactivation of markers [chloramphenicol acetyltransferase (CAT); hygromycin resistance (HYG(R))] at the resident H locus. For two STs, H locus markers were inactivated in less than 1% of the DTs, suggesting that, at these integration sites, H was relatively resistant to trans-inactivation. In contrast, the other two STs appeared to be more sensitive to trans-inactivation: 4-10% of the DTs were CAT(-) and/or Hyg(s). Inactivation of H locus markers could be attributed to two distinct phenomena: 1. Regeneration from cells containing different epigenetic states of H, in which either both, one or none of the H alleles was active. This instability in the expression of the H locus, which was independent of K, was more pronounced in the homozygous state, and was associated with cellular mosaicism of expression and methylation. 2. The presence of an unlinked K locus could weaken the Hyg(R) phenotype by transcriptional inactivation and increased methylation of the hph gene at the H locus. These results indicated that a susceptible transgene locus is inherently unstable and partially methylated, and that these characteristics are exacerbated when the locus is homozygous for the transgene and/or when an unlinked homologous transgene is present.", 
"An illustrative list is presented of human and animal studies which each point to the existence of a third source, in addition to genetic and environmental factors, underlying phenotypic differences in development. It is argued that this third source may consist of nonlinear epigenetic processes that can create variability at all phenotypical-somatic and behavioral-levels. In a quantitative genetic analysis with human subjects, these processes are confounded with within-family environmental influences. A preliminary model to quantify these influences is introduced.", 
"Analysis of the developmental capacities of androgenetic and gynogenetic mouse embryos (bearing two paternal or two maternal pronuclei, respectively) revealed a defect in blastocyst formation of androgenetic, but not gynogenetic, embryos that was a function of the maternal genotype. Androgenetic embryos constructed using fertilized eggs from C57BL/6 or (B6D2)F1 mice developed to the blastocyst stage at frequencies similar to those previously reported, whereas androgenetic embryos constructed with fertilized eggs from DBA/2 mice developed poorly, the majority failing to progress beyond the 16-cell stage and unable to form a blastocoel-like cavity, regardless of whether the male pronuclei were of C57BL6 or DBA/2 origin. This impaired development was observed even in androgenetic embryos constructed by transplanting two male pronuclei from fertilized DBA/2 eggs to enucleated C57BL/6 eggs, indicating that the defect cannot be explained as the lack of some essential component in the DBA/2 cytoplasm that might otherwise compensate for androgeny. Rather, the DBA/2 egg cytoplasm apparently modifies the incoming male pronuclei differently than does C57BL/6 egg cytoplasm. Several specific alterations in the protein synthesis pattern of DBA/2 androgenones were observed that reflect a defect in the regulatory mechanisms that normally modulate the synthesis of these proteins between the 8-cell and blastocyst stages. These results are consistent with a model in which cytoplasmic factors present in the egg direct a strain-dependent modification of paternal genome function in response to epigenetic modifications (genomic imprinting) established during gametogenesis and indicate that preimplantation development can be affected by these modifications at both the morphological and biochemical levels.", 
"Functional consequences of either suppressing or intensifying spontaneous neuronal firing have been studied in developing rat cerebral cortex cultures using, respectively, tetrodotoxin (TTX) and picrotoxin (PTX) added chronically to the growth medium. Simple measures derived from the interspike interval histogram were able to powerfully discriminate between age and treatment groups. After return to control medium, most TTX-treated neurons spontaneously displayed stereotyped clustering of action potentials ('phasic' firing) which closely resembled the characteristic firing patterns seen acutely in the presence of PTX. The 'TTX-syndrome' thus suggests that GABAergic synaptic inhibition is ineffective in cortical networks grown under conditions which prevent the expression of bioelectric activity. In contrast, after return to control medium, neurons which had been partially disinhibited throughout development (by continuous exposure to PTX) had even less phasic firing than was measured in age-matched controls. Based upon these and previous findings, a two (main) factor model is put forth which can economically account for the major effects. The working hypothesis embodied in this model is that phasic neuronal discharges not only accelerate the maturation of excitatory connections within the neocortex but, even more important, are crucial for the development of adequate inhibitory synaptic transmission.", 
"Differences in the activity of maternally and paternally derived genomes in maize endosperm have been observed at three levels of genetic manipulation. When the balance of entire chromosome sets departs from the standard ratio of two of maternal origin to one of paternal origin, development is impaired, often leading to seed failure. At the level of individual chromosomes, absence of a paternal representative for 8 of the 19 chromosome arms tested causes a marked reduction in kernel size. Replacement of the missing arms by ones of maternal origin does not complement this defect. At the gene level, some alleles of R confer solid coloration on the aleurone layer when transmitted maternally but patchy coloration (mottled) when transmitted via pollen. In contrast with the endosperm, no effect of parentage on R phenotype has been detected in embryonic and seedling tissues. Furthermore, gynogenetic and androgenetic haploid plants are viable in maize and are similar in appearance. The detection of parental effects in the endosperm, but not the embryo, points to the few cell divisions of the gametophytes as a critical stage in imprinting. Chromosomally based epigenetic variation originating at this stage would be reflected as imprinting effects. A separate fertilization establishes a line of genetic descent in the embryo that appears to be relatively free of imprinted genes.", 
" ", 
"Herein we describe a general multivariate quantitative genetic model that incorporates two potentially important developmental phenomena, maternal effects and epigenetic effects. Maternal and epigenetic effects are defined as partial regression coefficients and phenotypic variances are derived in terms of age-specific genetic and environmental variances. As a starting point, the traditional quantitative genetic model of additive gene effects and random environmental effects is cast in a developmental time framework. From this framework, we first extend a maternal effects model to include multiple developmental ages for the occurrence of maternal effects. An example of maternal effects occurring at multiple developmental ages is prenatal and postnatal maternal effects in mammals. Subsequently, a model of intrinsic and epigenetic effects in the absence of maternal effects is described. It is shown that genetic correlations can arise through epigenetic effects, and in the absence of other developmental effects, epigenetic effects are in general confounded with age-specific intrinsic genetic effects. Finally, the two effects are incorporated into the basic quantitative genetic model. For this more biologically realistic model combining maternal and epigenetic effects, it is shown that the phenotypic regressions of offspring on mother and offspring on father can be used in some cases to estimate simultaneously maternal effects and epigenetic effects.", 
"Butylated hydroxyanisole (BHA) is a synthetic food antioxidant used to prevent oils, fats and shortenings from oxidative deterioration and rancidity. This review depicts the current knowledge on BHA. The physical and chemical characteristics of BHA are summarized and its function as a food antioxidant is made clear. The toxicological characteristics of BHA and its metabolic fate in man and animal are briefly reviewed. Special emphasis is laid on the carcinogenicity of BHA in the forestomach of rodents and to related events in the forestomach and other tissues in experimental animals. At present there is sufficient evidence for carcinogenicity of BHA, but there is hardly any indication that BHA is genotoxic. Therefore risk assessment for this epigenetic carcinogen is based on non-stochastic principles. However, the mechanism underlying the tumorigenicity of BHA is not known. In the last part of this review an attempt is made to unravel the unknown mechanism of carcinogenicity. It is hypothesized that BHA gives rise to tumor formation in rodent forestomach by inducing heritable changes in DNA. Evidence is being provided that reactive oxygen species, in particular hydroxylradicals, may play a crucial role. The key question with respect to risk assessment for BHA is whether or not the underlying mechanism is thresholded, which is important for the choice of the appropriate model to assess the risk, if any, for man and to manage any potential risk.", 
]


In [8]:
###import pandas as pd

###df = pd.read_excel (r'C:/Users/brady/Desktop/TM/Evo-Bio All Time/Test1.xlsx')
###print (df)

In [9]:
print(df)

['Chronic inflammation is involved in the onset and development of many diseases, including obesity, atherosclerosis, type 2 diabetes, osteoarthritis, autoimmune and degenerative diseases, asthma, periodontitis, and cirrhosis. The inflammation process is mediated by chemokines, cytokines, and different inflammatory cells. Although the molecules and mechanisms that regulate this primary defense mechanism are not fully understood, recent findings offer a putative role of noncoding RNAs, especially microRNAs (miRNAs), in the progression and management of the inflammatory response. These noncoding RNAs are crucial for the stability and maintenance of gene expression patterns that characterize some cell types, tissues, and biologic responses. Several miRNAs, such as miR-126, miR-132, miR-146, miR-155, and miR-221, have emerged as important transcriptional regulators of some inflammation-related mediators. Additionally, little is known about the involvement of long noncoding RNAs, long inter

In [10]:
###CLEAN DATA###

In [11]:
# Convert to list
data = [simple_preprocess(doc) for doc in df]

In [12]:
print(data)

[['chronic', 'inflammation', 'is', 'involved', 'in', 'the', 'onset', 'and', 'development', 'of', 'many', 'diseases', 'including', 'obesity', 'atherosclerosis', 'type', 'diabetes', 'osteoarthritis', 'autoimmune', 'and', 'degenerative', 'diseases', 'asthma', 'periodontitis', 'and', 'cirrhosis', 'the', 'inflammation', 'process', 'is', 'mediated', 'by', 'chemokines', 'cytokines', 'and', 'different', 'inflammatory', 'cells', 'although', 'the', 'molecules', 'and', 'mechanisms', 'that', 'regulate', 'this', 'primary', 'defense', 'mechanism', 'are', 'not', 'fully', 'understood', 'recent', 'findings', 'offer', 'putative', 'role', 'of', 'noncoding', 'rnas', 'especially', 'micrornas', 'mirnas', 'in', 'the', 'progression', 'and', 'management', 'of', 'the', 'inflammatory', 'response', 'these', 'noncoding', 'rnas', 'are', 'crucial', 'for', 'the', 'stability', 'and', 'maintenance', 'of', 'gene', 'expression', 'patterns', 'that', 'characterize', 'some', 'cell', 'types', 'tissues', 'and', 'biologic', 'r

In [13]:
###MAY NEED CLEANING STEP, MAY NOT BECAUSE ABSTRACTS ARE SO CLEAN###

In [14]:
def sent_to_words(sentences):
    for sentence in sentences:
        yield(gensim.utils.simple_preprocess(str(sentence), deacc=True))  # deacc=True removes punctuations

data_words = list(sent_to_words(data))

print(data_words[:1])

[['chronic', 'inflammation', 'is', 'involved', 'in', 'the', 'onset', 'and', 'development', 'of', 'many', 'diseases', 'including', 'obesity', 'atherosclerosis', 'type', 'diabetes', 'osteoarthritis', 'autoimmune', 'and', 'degenerative', 'diseases', 'asthma', 'periodontitis', 'and', 'cirrhosis', 'the', 'inflammation', 'process', 'is', 'mediated', 'by', 'chemokines', 'cytokines', 'and', 'different', 'inflammatory', 'cells', 'although', 'the', 'molecules', 'and', 'mechanisms', 'that', 'regulate', 'this', 'primary', 'defense', 'mechanism', 'are', 'not', 'fully', 'understood', 'recent', 'findings', 'offer', 'putative', 'role', 'of', 'noncoding', 'rnas', 'especially', 'micrornas', 'mirnas', 'in', 'the', 'progression', 'and', 'management', 'of', 'the', 'inflammatory', 'response', 'these', 'noncoding', 'rnas', 'are', 'crucial', 'for', 'the', 'stability', 'and', 'maintenance', 'of', 'gene', 'expression', 'patterns', 'that', 'characterize', 'some', 'cell', 'types', 'tissues', 'and', 'biologic', 'r

In [15]:
###THIS STEP NEEDS TO BE CAREFULLY MONITORED TO MAKE SURE IT'S WORKING AS INTENDED###

In [16]:
# Build the bigram and trigram models
bigram = gensim.models.Phrases(data_words, min_count=5, threshold=100) # higher threshold fewer phrases.
trigram = gensim.models.Phrases(bigram[data_words], threshold=100)  

# Faster way to get a sentence clubbed as a trigram/bigram
bigram_mod = gensim.models.phrases.Phraser(bigram)
trigram_mod = gensim.models.phrases.Phraser(trigram)

# See trigram example
print(trigram_mod[bigram_mod[data_words[0]]])

['chronic', 'inflammation', 'is', 'involved', 'in', 'the', 'onset', 'and', 'development', 'of', 'many', 'diseases', 'including', 'obesity', 'atherosclerosis', 'type_diabetes', 'osteoarthritis', 'autoimmune', 'and', 'degenerative', 'diseases', 'asthma', 'periodontitis', 'and', 'cirrhosis', 'the', 'inflammation', 'process', 'is', 'mediated', 'by', 'chemokines', 'cytokines', 'and', 'different', 'inflammatory', 'cells', 'although', 'the', 'molecules', 'and', 'mechanisms', 'that', 'regulate', 'this', 'primary', 'defense', 'mechanism', 'are', 'not', 'fully', 'understood', 'recent', 'findings', 'offer', 'putative', 'role', 'of', 'noncoding_rnas', 'especially', 'micrornas', 'mirnas', 'in', 'the', 'progression', 'and', 'management', 'of', 'the', 'inflammatory', 'response', 'these', 'noncoding_rnas', 'are', 'crucial', 'for', 'the', 'stability', 'and', 'maintenance', 'of', 'gene', 'expression', 'patterns', 'that', 'characterize', 'some', 'cell', 'types', 'tissues', 'and', 'biologic', 'responses',

In [17]:
# Define functions for stopwords, bigrams, trigrams and lemmatization
def remove_stopwords(texts):
    return [[word for word in simple_preprocess(str(doc)) if word not in stop_words] for doc in texts]

def make_bigrams(texts):
    return [bigram_mod[doc] for doc in texts]

def make_trigrams(texts):
    return [trigram_mod[bigram_mod[doc]] for doc in texts]

def lemmatization(texts, allowed_postags=['NOUN', 'ADJ', 'VERB', 'ADV']):
    """https://spacy.io/api/annotation"""
    texts_out = []
    for sent in texts:
        doc = nlp(" ".join(sent)) 
        texts_out.append([token.lemma_ for token in doc if token.pos_ in allowed_postags])
    return texts_out

In [18]:
###en_core_web_sm needs to be explicitly loaded and I believe you need to use "python -m spacy download en" in cmd.exe to properly load everything.###

In [19]:
# Remove Stop Words
data_words_nostops = remove_stopwords(data_words)

# Form Bigrams
data_words_bigrams = make_bigrams(data_words_nostops)

# Initialize spacy 'en' model, keeping only tagger component (for efficiency)
# python3 -m spacy download en
nlp = spacy.load('en_core_web_sm', disable=['parser', 'ner'])

# Do lemmatization keeping only noun, adj, vb, adv
data_lemmatized = lemmatization(data_words_bigrams, allowed_postags=['NOUN', 'ADJ', 'VERB', 'ADV'])

print(data_lemmatized[:1])

[['chronic', 'inflammation', 'involve', 'onset', 'development', 'many', 'disease', 'include', 'obesity', 'atherosclerosis', 'osteoarthritis', 'autoimmune', 'degenerative', 'disease', 'cirrhosis', 'inflammation', 'process', 'mediate', 'chemokine', 'cytokine', 'different', 'inflammatory', 'cell', 'molecule', 'mechanism', 'regulate', 'primary', 'defense', 'mechanism', 'fully', 'understand', 'recent', 'finding', 'offer', 'putative', 'role', 'especially', 'microrna', 'mirna', 'progression', 'management', 'inflammatory', 'response', 'crucial', 'stability', 'maintenance', 'gene', 'expression', 'pattern', 'characterize', 'cell', 'type', 'tissue', 'biologic', 'response', 'several', 'mirna', 'emerge', 'important', 'transcriptional', 'regulator', 'inflammation', 'relate', 'mediator', 'additionally', 'little', 'know', 'involvement', 'long', 'long', 'intergenic', 'circular', 'mediate', 'process', 'homeostatic', 'imbalance', 'associate', 'disorder', 'emerge', 'biomarker', 'diagnosis', 'value', 'prog

In [20]:
# Create Dictionary
id2word = corpora.Dictionary(data_lemmatized)

# Create Corpus
texts = data_lemmatized

# Term Document Frequency
corpus = [id2word.doc2bow(text) for text in texts]

# View
print(corpus[:1])

[[(0, 1), (1, 1), (2, 1), (3, 1), (4, 1), (5, 1), (6, 1), (7, 1), (8, 1), (9, 1), (10, 1), (11, 2), (12, 1), (13, 1), (14, 1), (15, 1), (16, 1), (17, 1), (18, 1), (19, 1), (20, 1), (21, 1), (22, 1), (23, 1), (24, 1), (25, 3), (26, 1), (27, 2), (28, 1), (29, 1), (30, 1), (31, 1), (32, 1), (33, 1), (34, 1), (35, 1), (36, 1), (37, 1), (38, 1), (39, 1), (40, 1), (41, 1), (42, 6), (43, 2), (44, 1), (45, 1), (46, 1), (47, 1), (48, 1), (49, 1), (50, 1), (51, 2), (52, 1), (53, 1), (54, 1), (55, 2), (56, 2), (57, 2), (58, 1), (59, 3), (60, 1), (61, 1), (62, 1), (63, 1), (64, 1), (65, 1), (66, 1), (67, 1), (68, 2), (69, 1), (70, 1), (71, 1), (72, 1), (73, 1), (74, 1), (75, 1), (76, 2), (77, 1), (78, 1), (79, 3), (80, 2), (81, 1), (82, 1), (83, 1), (84, 1), (85, 1), (86, 1), (87, 1), (88, 1), (89, 1), (90, 2), (91, 1), (92, 1), (93, 1)]]


In [21]:
#to call an individual dictionary term switch value as appropriate
id2word[0]

'activator'

In [22]:
# Human readable format of corpus (term-frequency)
[[(id2word[id], freq) for id, freq in cp] for cp in corpus[:1]]

[[('activator', 1),
  ('additionally', 1),
  ('adhesion', 1),
  ('alpha', 1),
  ('alteration', 1),
  ('antagonism', 1),
  ('associate', 1),
  ('atherosclerosis', 1),
  ('autoimmune', 1),
  ('biologic', 1),
  ('biomarker', 1),
  ('cell', 2),
  ('characterize', 1),
  ('chemokine', 1),
  ('chronic', 1),
  ('circular', 1),
  ('cirrhosis', 1),
  ('context', 1),
  ('crucial', 1),
  ('cytokine', 1),
  ('defense', 1),
  ('degenerative', 1),
  ('development', 1),
  ('diagnosis', 1),
  ('different', 1),
  ('disease', 3),
  ('disorder', 1),
  ('emerge', 2),
  ('emphasis', 1),
  ('especially', 1),
  ('exogenous', 1),
  ('expression', 1),
  ('field', 1),
  ('finding', 1),
  ('fully', 1),
  ('future', 1),
  ('gene', 1),
  ('highlight', 1),
  ('homeostatic', 1),
  ('imbalance', 1),
  ('important', 1),
  ('include', 1),
  ('inflammation', 6),
  ('inflammatory', 2),
  ('inhibitor', 1),
  ('intercellular', 1),
  ('intergenic', 1),
  ('involve', 1),
  ('involvement', 1),
  ('know', 1),
  ('little', 1),
 

In [23]:
###Loads of room for customization at this step. Read carefully and adjust accordingly.###

In [24]:
# Build LDA model
lda_model = gensim.models.ldamodel.LdaModel(corpus=corpus,
                                           id2word=id2word,
                                           num_topics=20, 
                                           random_state=100,
                                           update_every=1,
                                           chunksize=100,
                                           passes=10,
                                           alpha='auto',
                                           per_word_topics=True)

In [25]:
# Print the Keyword in the topics
pprint(lda_model.print_topics())
doc_lda = lda_model[corpus]

[(0,
  '0.152*"sex" + 0.069*"selective" + 0.028*"redundancy" + 0.020*"theme" + '
  '0.018*"immunity" + 0.014*"receive" + 0.011*"ligand" + 0.008*"signal" + '
  '0.008*"neuroendocrine" + 0.006*"pressure"'),
 (1,
  '0.102*"age" + 0.090*"model" + 0.052*"developmental" + 0.038*"quantitative" '
  '+ 0.037*"male" + 0.027*"derive" + 0.025*"development" + 0.025*"intrinsic" + '
  '0.025*"develop" + 0.024*"neuronal"'),
 (2,
  '0.064*"proliferation" + 0.058*"metastasis" + 0.039*"transformation" + '
  '0.032*"invasion" + 0.021*"hallmark" + 0.019*"drug_resistance" + '
  '0.018*"good" + 0.013*"twin" + 0.010*"compelling" + 0.010*"noncoding_rna"'),
 (3,
  '0.031*"telomere" + 0.027*"length" + 0.026*"temperature" + 0.023*"cultured" '
  '+ 0.022*"stimulus" + 0.020*"ecology" + 0.017*"dysfunction" + '
  '0.015*"telomeric" + 0.014*"spatial" + 0.014*"namely"'),
 (4,
  '0.075*"blastocyst" + 0.067*"defect" + 0.055*"impair" + 0.035*"bear" + '
  '0.028*"modulate" + 0.028*"underlying" + 0.027*"fat" + 0.023*"freque

In [26]:
###Model perplexity and topic coherence provide a convenient measure to judge how good a given topic model is. 
###In my experience, topic coherence score, in particular, has been more helpful.

###Need to learn more about these values.

In [27]:
# Compute Perplexity
print('\nPerplexity: ', lda_model.log_perplexity(corpus))  # a measure of how good the model is. lower the better.

# Compute Coherence Score
coherence_model_lda = CoherenceModel(model=lda_model, texts=data_lemmatized, dictionary=id2word, coherence='c_v')
coherence_lda = coherence_model_lda.get_coherence()
print('\nCoherence Score: ', coherence_lda)


Perplexity:  -11.264235389665757

Coherence Score:  0.4227585407830062


In [28]:
pyLDAvis.enable_notebook()
vis = pyLDAvis.gensim.prepare(lda_model, corpus, id2word)
vis

C:\Users\brady\Anaconda3\lib\site-packages\pyLDAvis\_prepare.py:232: FutureWarning: In a future version of pandas all arguments of DataFrame.drop except for the argument 'labels' will be keyword-only
  head(R).drop('saliency', 1)


PreparedData(topic_coordinates=              x         y  topics  cluster       Freq
topic                                                
18    -0.289194  0.102627       1        1  38.588122
6     -0.273049  0.076717       2        1  16.645943
16    -0.294646  0.192168       3        1  15.395548
7     -0.172333  0.168308       4        1   6.282900
13    -0.174261 -0.216950       5        1   5.864502
10    -0.097618 -0.100461       6        1   4.627222
17     0.044007  0.032338       7        1   2.601694
14    -0.122475 -0.122369       8        1   2.313529
1     -0.080960 -0.175955       9        1   2.062688
8     -0.043919 -0.245256      10        1   1.664740
4      0.064158 -0.007286      11        1   1.215485
5      0.140199  0.020149      12        1   0.868074
3      0.163373  0.033597      13        1   0.586824
2      0.165068  0.033902      14        1   0.399411
0      0.162941  0.036287      15        1   0.387218
9      0.165711  0.035170      16        1   0.259796
15     0.164625  0.035114      17        1   0.129808
12     0.160943  0.034290      18        1   0.063745
19     0.159005  0.033864      19        1   0.032535
11     0.158425  0.033747      20        1   0.010218, topic_info=                            Term         Freq        Total Category  logprob  \
263                  methylation  1434.000000  1434.000000  Default  30.0000   
115                          dna  1242.000000  1242.000000  Default  29.0000   
187                       effect   950.000000   950.000000  Default  28.0000   
11                          cell  1940.000000  1940.000000  Default  27.0000   
36                          gene  2129.000000  2129.000000  Default  26.0000   
...                          ...          ...          ...      ...      ...   
5627  microsatellite_instability     0.001324     0.787667  Topic20  -9.0432   
5626                        hmsh     0.001324     0.787654  Topic20  -9.0432   
5625              high_frequency     0.001324     0.787655  Topic20  -9.0432   
5624                unidentified     0.001324     0.787660  Topic20  -9.0432   
5623                   threonine     0.001324     0.787655  Topic20  -9.0432   

      loglift  
263      30.0  
115      29.0  
187      28.0  
11       27.0  
36       26.0  
...       ...  
5627      2.8  
5626      2.8  
5625      2.8  
5624      2.8  
5623      2.8  

[934 rows x 6 columns], token_table=      Topic      Freq       Term
term                            
1407      2  0.995015   aberrant
292       1  0.989439    ability
2355      7  0.996972       able
397       1  0.491472    absence
397      10  0.498919    absence
...     ...       ...        ...
1222     14  0.682408     worker
171       3  0.821657      yeast
171      12  0.144998      yeast
2488     16  0.820182  zinc_fing
1109      8  0.959696     zygote

[937 rows x 3 columns], R=30, lambda_step=0.01, plot_opts={'xlab': 'PC1', 'ylab': 'PC2'}, topic_order=[19, 7, 17, 8, 14, 11, 18, 15, 2, 9, 5, 6, 4, 3, 1, 10, 16, 13, 20, 12])

In [ ]:
###rename file.html before running command. Search computer and it should be in the user directory.
p = pyLDAvis.gensim.prepare(lda_model, corpus, id2word)
pyLDAvis.save_html(p, 'file.html')